#### PIPE - 11:    
This pipe covers the following : 
1. All features of pipe 10
2. Wrong Side detection
3. No Helmet detection

In [1]:
from utils.runner_utils import run_detection

In [9]:
video_path='/media/hlink/hd/test_videos/testx_vid_1.mp4'
ssd=[
     {'id': 3, 'name': 'car', 'vehicle_class': 'lmv'},
     {'id': 4, 'name': 'motorcycle', 'vehicle_class': 'mcwg/mcg'},
     {'id': 5, 'name': 'truck', 'vehicle_class': 'hgmv'},
     {'id': 6, 'name': 'bus', 'vehicle_class': 'hpmv'},
     {'id': 7, 'name': 'rikshaw', 'vehicle_class': 'l5m'}
    ]
voi=[
   {'id': 2, 'name': 'over_speed'}, 
   {'id': 3, 'name': 'no_helmet'}
]

In [3]:
run_detection(video_file_path=video_path,camera_id="4",area_id="56",vehicle_json_arr=ssd,violation_json_arr=voi,area_selection=True,debug=True)

2024-05-30 14:22:34.790 | SUCCESS  | boxmot.appearance.reid_model_factory:load_pretrained_weights:207 - Successfully loaded pretrained weights from "models/osnet_x0_25_msmt17.pt"


tracking_area_coordinates--[{'x_start': 307, 'y_start': 138, 'x_end': 764, 'y_end': 321}, {'x_start': 307, 'y_start': 188, 'x_end': 764, 'y_end': 270}]
entered if-
Starting video inference
ending video inference
{2: 220, 10: 252, 51: 1571, 65: 2463, 67: 2867, 87: 3692, 84: 3740, 93: 3818, 103: 4258, 104: 4336, 110: 4561, 116: 4883, 121: 4928, 134: 5575, 138: 5671, 136: 5688, 148: 6560, 149: 6773, 163: 7818, 186: 8775, 191: 9108, 253: 10537, 266: 10751, 278: 11382, 358: 14001, 359: 14107, 389: 14752}
Json format is maintained True
Debug Process 1 Completed
Debug Process 2 Completed
PRitning from video clips
PRitning from video clips
PRitning from video clips
PRitning from video clips
PRitning from video clips
PRitning from video clips
PRitning from video clips
PRitning from video clips
PRitning from video clips
PRitning from video clips
PRitning from video clips
PRitning from video clips
PRitning from video clips
PRitning from video clips
PRitning from video clips
PRitning from video cl

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



Debug Process 4 Completed
Debug Process 6 Completed


KeyboardInterrupt: 

Process Process-3:
Traceback (most recent call last):
  File "/usr/lib/python3.11/multiprocessing/process.py", line 314, in _bootstrap
    self.run()
  File "/usr/lib/python3.11/multiprocessing/process.py", line 108, in run
    self._target(*self._args, **self._kwargs)
  File "/home/hlink/workspace/learning/boxmot/utils/mt_image_enhancement.py", line 25, in sub_process_image_enhance_using_dnn_supress_cpu
    enhance_image_using_dnn_superres(image_path=i,save_dir_path=temp_dir_path,model_path='models/EDSR_x4.pb')
  File "/home/hlink/workspace/learning/boxmot/utils/dnn_superres_utils.py", line 16, in enhance_image_using_dnn_superres
    upscaled_img = sr.upsample(image)
                   ^^^^^^^^^^^^^^^^^^
KeyboardInterrupt
Process Process-7:
Traceback (most recent call last):
  File "/usr/lib/python3.11/multiprocessing/process.py", line 314, in _bootstrap
    self.run()
  File "/usr/lib/python3.11/multiprocessing/process.py", line 108, in run
    self._target(*self._args, **self._kwarg

In [ ]:
'models/yolov8s.pt'

In [1]:
import cv2
import numpy as np
import torch
import time

from ultralytics import YOLO

from utils.back_all_utils import json_to_csv, speed_calculator_kmph
from utils.blurring_utils import blur_except_rectangle
from utils.checker_utils import json_frame_order_checker
from utils.conversion_utils import  csv_to_json_arr, object_class_name_normalizer, violation_based_json_creator
from utils.date_time_utils import get_current_date, video_time_checker
from utils.file_utils import create_directory, detection_coordinate_write, evidance_directories_creator, evidance_img_separator
from utils.image_deblur_utils import deblur_images
from utils.json_utils import final_json_processor, ocr_result_filter, remove_empty_from_dict, voilation_capture_json_creator
from utils.model_utils import remove_model_from_gpu
from utils.mt_anrp_utils import main_process_detecting_and_cropping_liscense_plate, main_process_ocr_scanner_for_liscense_plate
from utils.mt_image_enhancement import main_process_image_enhance_using_dnn_supress_cpu
from utils.mt_image_utils import main_process_crop_images_using_paths, main_process_threshold_image_creator_using_paths
from utils.mt_video_utils import main_process_video_clip_creator
from utils.plotting_utils import line_plotter, plot_tracks, prediction_coordinated_hadler, tracker_element_handler
from utils.rectangle_utils import draw_rectangle_on_first_frame
from utils.tracker_utils import tracker_init
from utils.image_utils import blurred_frame_writer, frame_writer

video_file_path='testx_vid_1.mp4'
vehicle_json_arr=[
     {'id': 3, 'name': 'car', 'vehicle_class': 'lmv'},
     {'id': 4, 'name': 'motorcycle', 'vehicle_class': 'mcwg/mcg'},
     {'id': 5, 'name': 'truck', 'vehicle_class': 'hgmv'},
     {'id': 6, 'name': 'bus', 'vehicle_class': 'hpmv'},
     {'id': 7, 'name': 'rikshaw', 'vehicle_class': 'l5m'}
    ]
violation_json_arr=[
   {'id': 2, 'name': 'over_speed'}, 
   {'id': 3, 'name': 'no_helmet'}
]
gpu_device_number=0
debug=True
down = {}
up = {}
tracking_area_coordinates=None
text_color = (0, 0, 0)  # Black color for text
yellow_color = (0, 255, 255)  # Yellow color for background
red_color = (0, 0, 255)  # Red color for lines
blue_color = (255, 0, 0)  # Blue color for lines
area_id=-1
camera_id=-1

counter_down = []
counter_up = []


offset = 6
# Specify the start and end points of the line
start_point = (300, 198)
end_point = (300, 280)

outer_x_start=321
outer_x_end=801
outer_y_start=129
outer_y_end=416

inner_x_start=321
inner_x_end=801
inner_y_start=231
inner_y_end=313
  
video_width=1020
video_height=500
frame_count=0
area_selection=True
all_id_tracker=[]
voilation_id_tracker=[]
violation_frame_tracker={}
violation_frame_tracker_for_helmet_detection={}
main_violation_tracker_json={}
if area_selection:
    tracking_area_coordinates= draw_rectangle_on_first_frame(video_file_path, video_width, video_height)
    print(f"tracking_area_coordinates--{tracking_area_coordinates}")
    if tracking_area_coordinates:
            print("entered if-")
            outer_x_start=tracking_area_coordinates[0]['x_start']
            outer_x_end=tracking_area_coordinates[0]['x_end']
            outer_y_start=tracking_area_coordinates[0]['y_start']
            outer_y_end=tracking_area_coordinates[0]['y_end']
            inner_x_start=tracking_area_coordinates[1]['x_start']
            inner_x_end=tracking_area_coordinates[1]['x_end']
            inner_y_start=tracking_area_coordinates[1]['y_start']
            inner_y_end=tracking_area_coordinates[1]['y_end']
    

        
    
vehicle_class_json=violation_based_json_creator(vehicle_json_arr)
violation_type_json=violation_based_json_creator(violation_json_arr)

tracker=tracker_init(cuda_device=torch.cuda.is_available(),cuda_device_number=gpu_device_number)
# model=YOLO('models/custom_vehicle_detection.pt')
model=YOLO('models/yolov8n.pt')

                    yolo_model_classes=model.names
  

cap = cv2.VideoCapture(video_file_path)
assert cap.isOpened(), "Error reading video file"

fourcc = cv2.VideoWriter_fourxcc(*'XVID')
out_main = cv2.VideoWriter('output_strongs.avi', fourcc, 20.0, (1020, 500))
all_frames_record_path=create_directory('all_frames_record')
violation_frames_record_path=create_directory('all_violation_record')
current_date=get_current_date()
if debug:
    print("Starting video inference")
    
while True:    
        ret, frame = cap.read()

        if not ret:
            break
        
        resized_image=cv2.resize(frame,(video_width, video_height))
        blurred_image=blur_except_rectangle(resized_image,outer_x_start,outer_y_start,outer_x_end,outer_y_end,offset_size=[0,80],blur_kernel_size=(50,50))
        
        # results=model.predict(blurred_image,conf=0.4,verbose=False,device=[gpu_device_number],classes=[2,3])
        results=model.predict(blurred_image,conf=0.4,verbose=False,device=[0],classes=[2,3])
        # print(f"\n----------------------------------------------------------------------------------\nResult without detection \n{results[0].boxes.data}\n----------------------------------------------------------------------------------\n")
        blurred_image=line_plotter(frame=blurred_image,x_start=inner_x_start,x_end=inner_x_end,y=inner_y_start,line_color=red_color,line_name='boundry 1',line_thickness=2,text_color=text_color)
        blurred_image=line_plotter(frame=blurred_image,x_start=inner_x_start,x_end=inner_x_end,y=inner_y_end,line_color=blue_color,line_name='boundry 2',line_thickness=2,text_color=text_color)
        
        # Specify the color of the line in BGR format (here, it's white)
        color = (255, 255, 255)
        
        # Draw the vertical line on the image
        thickness = 2  # You can adjust the thickness as needed
        cv2.line(blurred_image, start_point, end_point, color, thickness)
        
        # im=cv2.rectangle(blurred_image, (300, 198), (800, 280), (255, 255, 255), 2)
        
        px,conf=prediction_coordinated_hadler(results)
        dets = []
        # Experimenting
        dets,object_class_id=tracker_element_handler(dets,px,conf)        
        
        # print('out_from')
        
        dets = np.array(dets)
        # print(dets)
        if len(dets) > 0:
            tracks = tracker.update(dets, blurred_image) # --> M X (x, y, x, y, id, conf, cls, ind)
            # print('tracks',tracks)    
            for track in tracks:
                    travel_direction=-1
                    
                    blurred_image,object_id,cx,cy,bbox_list,object_class=plot_tracks(track,blurred_image,debug=True)
                    
                    object_class=int(object_class)

                    if f'{object_id}' in main_violation_tracker_json:
                        pass
                    else:
                        main_violation_tracker_json[f'{object_id}']={}
                        #Remember by adding this we are trying to handle multiple violations in a single array
                        #We also need to improvde the checker utils and 
                        main_violation_tracker_json[f'{object_id}']['violation_type_id']=[]
                        # print("adding Id to tracker")
                    all_id_tracker.append(object_id)
                    
                    # Adding file path for csv
                    all_detections_track_csv=detection_coordinate_write(frame_count,object_id,bbox_list,object_class,f'{current_date}_all_frame_detection_detail.csv')
                
                    if inner_y_start<(cy+offset) and inner_y_start > (cy-offset):
                        # print("entered if 1")
                        down[object_id]=time.time()
                
                    if object_id in down:
                        # print("entered if 2")
                
                        if inner_y_end<(cy+offset) and inner_y_end > (cy-offset):
                            # print("entered if 3")
                            travel_direction=1
                            elapsed_time=time.time() - down[object_id] 
                            # print("entered if 4")
                            if counter_down.count(object_id)==0:
                                counter_down.append(object_id) 
                                distance = 9
                                est_speed=speed_calculator_kmph(distance,elapsed_time)
                                if est_speed>20:
                                    
                                    # Fucntion for timer tracking
                                    time_dict=video_time_checker(count=frame_count,cap=cap)
                                    
                                    # Getting the name for the detected object
                                    object_name=object_class_name_normalizer(object_class_id,yolo_model_classes)
                                    
                                                main_violation_tracker_json[f'{object_id}']['violation_type_id'].append(violation_type_json['over_speed'])
                                    main_violation_tracker_json[f'{object_id}']['vehicle_type_id']=vehicle_class_json[f'{object_name}']
                                    
                                    main_violation_tracker_json[f'{object_id}']['vehicle_speed']=est_speed
                                    main_violation_tracker_json[f'{object_id}']['travel_direction']=travel_direction

                                    main_violation_tracker_json[f'{object_id}']['location_id']=area_id
                                    main_violation_tracker_json[f'{object_id}']['camera_id']=camera_id

                                    main_violation_tracker_json[f'{object_id}']['violation_date']=current_date
                                    main_violation_tracker_json[f'{object_id}']['violation_time']=time_dict['time']
                                    
                                    voilation_id_tracker.append(object_id)
                                    
                                    violation_frame_tracker[object_id]=frame_count
                                    violation_frame_tracker_for_helmet_detection[object_id]=[frame_count,object_name]
                                    violation_frame_writer_original=frame_writer(frame_count,resized_image,violation_frames_record_path)
                                    violation_frame_writer_blurred=blurred_frame_writer(frame_count,resized_image,violation_frames_record_path,bbox_list=bbox_list)
                                    
                                    main_violation_tracker_json[f'{object_id}']['evidence_focused_image_url']=violation_frame_writer_blurred
                                    main_violation_tracker_json[f'{object_id}']['evidence_image_url']=violation_frame_writer_original
                                                
                                    violation_csv_file_path=detection_coordinate_write(frame_count,object_id,bbox_list,object_class,f'{current_date}_violation_frame_detection_detail.csv')
                                    
                                # print(f"for {object_id} speed is -> {est_speed}")
        
        _=frame_writer(frame_count,resized_image,all_frames_record_path)    
        frame_count+=1
        out_main.write(resized_image)
        
        # # break on pressing q or spaceq
        cv2.imshow('Strong Sort Detection', blurred_image)     
        # key = cv2.waitKey(25) & 0xFF
        
        if cv2.waitKey(20) & 0xFF == ord('q'):
            break
cap.release()
cv2.destroyAllWindows()
remove_model_from_gpu(model)
if debug:
        print("ending video inference")
print(violation_frame_tracker)
main_violation_json=voilation_capture_json_creator(voilation_id_tracker,all_detections_track_csv)
maintained=json_frame_order_checker(main_violation_json)
if debug:
        print(f"Json format is maintained {maintained}")
if maintained:
        # Function for creating dir paths only
    evidance_img_dir_paths,evidance_clip_dir_paths=evidance_directories_creator(main_violation_json)
    if debug:
            print("Debug Process 1 Completed")
        # Function for taking separating image
        ### This should also add vehicle class name while making the folders 
    evidance_img_dir_paths=evidance_img_separator(evidance_img_dir_paths,all_frames_record_path,main_violation_json)   
        
    if debug:
            print("Debug Process 2 Completed")
        
    violation_coordinates_json=csv_to_json_arr(file_path=all_detections_track_csv,violation_json=violation_frame_tracker)
    print(f'{voilation_id_tracker},{violation_frame_tracker},{evidance_clip_dir_paths},{all_frames_record_path},{violation_coordinates_json}')
        #####################################################################################################
        #####################################################################################################
        #####################################################################################################
        #####################################################################################################
        #####################################################################################################
        #####################################################################################################
        #####################################################################################################
    main_process_video_clip_creator(voilation_id_tracker,violation_frame_tracker,evidance_clip_dir_paths,all_frames_record_path,violation_coordinates_json)
        #####################################################################################################
        #####################################################################################################
        #####################################################################################################
        #####################################################################################################
        #####################################################################################################
        #####################################################################################################
        #####################################################################################################
        #####################################################################################################

    if debug:
            print("Debug Process 3 Completed")
        
    cropped_images_path_list=main_process_crop_images_using_paths(evidance_img_dir_paths,main_violation_json)
    if debug:
                print("Debug Process 4 Completed")
        
    deblurred_image_paths=deblur_images(cropped_images_path_list,main_violation_json)
    if debug:
            print("Debug Process 6 Completed")
        
        # Using default 8 threads to achive max effiencicy
    enhance_image_path=main_process_image_enhance_using_dnn_supress_cpu(deblurred_image_paths,num_threads=8)
    if debug:
            print("Debug Process 7 Completed")
        
    cropped_lp_paths=main_process_detecting_and_cropping_liscense_plate(enhance_image_path,'models/LPD.pt',2)
    if debug:
            print("Debug Process 8 Completed")
        
    enhanced_cropped_images_lp=main_process_image_enhance_using_dnn_supress_cpu(cropped_lp_paths,num_threads=8,dir_name='cropped_lp_enhanced')
    if debug:
            print("Debug Process 9 Completed")
        
    thresholded_image=main_process_threshold_image_creator_using_paths(enhanced_cropped_images_lp)
    if debug:
            print("Debug Process 10 Completed")
        
    lp_csv_path=main_process_ocr_scanner_for_liscense_plate(folder_paths=thresholded_image,threads=1,gpu_device_number=1)
    if debug:
            print("Debug Process 11 Completed")
        
    ocr_json=ocr_result_filter(main_violation_tracker_json,lp_csv_path)
    if debug:
            print("Debug Process 12 Completed")
        
    main_violation_tracker_json=final_json_processor(main_violation_tracker_json,ocr_json)
    if debug:
            print("Debug Process 13 Completed")
    main_violation_tracker_json=remove_empty_from_dict(main_violation_tracker_json)
    if debug:
            print("Debug Process 14 Completed")
    csv_file_name=f'{get_current_date()}_inference_results.csv'
    results_csv_path=json_to_csv(json_data=main_violation_tracker_json,csv_filename=f'{csv_file_name}',debug=True)

2024-05-31 09:07:42.510 | INFO     | boxmot.utils.torch_utils:select_device:52 - Yolo Tracking v10.0.71 🚀 Python-3.11.6 torch-2.2.2+cu121CPU
2024-05-31 09:07:42.579 | SUCCESS  | boxmot.appearance.reid_model_factory:load_pretrained_weights:207 - Successfully loaded pretrained weights from "models/osnet_x0_25_msmt17.pt"


tracking_area_coordinates--[{'x_start': 324, 'y_start': 134, 'x_end': 698, 'y_end': 273}, {'x_start': 324, 'y_start': 162, 'x_end': 698, 'y_end': 244}]
entered if-
Starting video inference
Ultralytics YOLOv8.2.26 🚀 Python-3.11.6 torch-2.2.2+cu121 


/home/wifee/workspace/Strong Sort tracker/sst/lib/python3.11/site-packages/torch/cuda/__init__.py:628: UserWarning: Can't initialize NVML
  warnings.warn("Can't initialize NVML")


ValueError: Invalid CUDA 'device=0' requested. Use 'device=cpu' or pass valid CUDA device(s) if available, i.e. 'device=0' or 'device=0,1,2,3' for Multi-GPU.

torch.cuda.is_available(): False
torch.cuda.device_count(): 0
os.environ['CUDA_VISIBLE_DEVICES']: -1
See https://pytorch.org/get-started/locally/ for up-to-date torch install instructions if no CUDA devices are seen by torch.


In [6]:
violation_json={1: 222, 6: 253, 41: 1572, 56: 2465, 61: 2868, 77: 3693, 75: 3742, 87: 3819, 94: 4259, 95: 4337, 101: 4562, 109: 4884, 105: 4888, 113: 4930, 123: 5576, 127: 5672, 125: 5689, 133: 6561, 136: 6774, 146: 7820, 165: 8776, 169: 9109, 214: 10538, 225: 10752, 241: 11384, 317: 14003, 318: 14109, 343: 14754}

In [2]:
violation_coordinates_json

[{'2': [['82', '2', '366', ' 103', ' 394', ' 125', '2'],
   ['83', '2', '366', ' 102', ' 395', ' 126', '2'],
   ['84', '2', '366', ' 103', ' 395', ' 127', '2'],
   ['85', '2', '367', ' 103', ' 395', ' 127', '2'],
   ['86', '2', '367', ' 104', ' 395', ' 127', '2'],
   ['87', '2', '367', ' 103', ' 396', ' 127', '2'],
   ['88', '2', '367', ' 103', ' 396', ' 127', '2'],
   ['89', '2', '367', ' 103', ' 396', ' 127', '2'],
   ['90', '2', '367', ' 103', ' 397', ' 127', '2'],
   ['91', '2', '367', ' 103', ' 398', ' 128', '2'],
   ['92', '2', '367', ' 103', ' 398', ' 128', '2'],
   ['93', '2', '366', ' 104', ' 398', ' 129', '2'],
   ['94', '2', '366', ' 104', ' 398', ' 130', '2'],
   ['95', '2', '367', ' 104', ' 399', ' 130', '2'],
   ['96', '2', '368', ' 105', ' 399', ' 130', '2'],
   ['97', '2', '368', ' 105', ' 399', ' 131', '2'],
   ['98', '2', '369', ' 106', ' 399', ' 131', '2'],
   ['99', '2', '369', ' 106', ' 400', ' 131', '2'],
   ['100', '2', '369', ' 107', ' 401', ' 132', '2'],
   ['1

In [14]:
file_path='29_05_2024_all_frame_detection_detail.csv'
with open(file_path,'r') as f:
    contents=f.read()

In [16]:
main_arr=contents.split('\n')
# print(type())
splitted_array=[i.split(',') for i in main_arr]
print(splitted_array)

[['77', '1', '364', ' 104', ' 394', ' 125', '2'], ['81', '1', '363', ' 103', ' 395', ' 125', '2'], ['82', '1', '364', ' 102', ' 396', ' 126', '2'], ['83', '1', '364', ' 102', ' 397', ' 126', '2'], ['84', '1', '364', ' 103', ' 397', ' 127', '2'], ['85', '1', '365', ' 103', ' 397', ' 127', '2'], ['86', '1', '365', ' 103', ' 397', ' 127', '2'], ['87', '1', '365', ' 103', ' 398', ' 127', '2'], ['88', '1', '365', ' 103', ' 398', ' 127', '2'], ['89', '1', '365', ' 102', ' 398', ' 127', '2'], ['90', '1', '366', ' 102', ' 398', ' 127', '2'], ['91', '1', '365', ' 103', ' 399', ' 128', '2'], ['92', '1', '365', ' 103', ' 399', ' 128', '2'], ['93', '1', '365', ' 104', ' 398', ' 129', '2'], ['94', '1', '365', ' 104', ' 399', ' 129', '2'], ['95', '1', '365', ' 104', ' 399', ' 130', '2'], ['96', '1', '366', ' 105', ' 399', ' 130', '2'], ['97', '1', '367', ' 105', ' 400', ' 131', '2'], ['98', '1', '368', ' 106', ' 399', ' 131', '2'], ['99', '1', '368', ' 106', ' 400', ' 131', '2'], ['100', '1', '369',

In [46]:
splitted_array=[i.split(',') for i in contents.split('\n')]
print(splitted_array)

[['77', '1', '364', ' 104', ' 394', ' 125', '2'], ['81', '1', '363', ' 103', ' 395', ' 125', '2'], ['82', '1', '364', ' 102', ' 396', ' 126', '2'], ['83', '1', '364', ' 102', ' 397', ' 126', '2'], ['84', '1', '364', ' 103', ' 397', ' 127', '2'], ['85', '1', '365', ' 103', ' 397', ' 127', '2'], ['86', '1', '365', ' 103', ' 397', ' 127', '2'], ['87', '1', '365', ' 103', ' 398', ' 127', '2'], ['88', '1', '365', ' 103', ' 398', ' 127', '2'], ['89', '1', '365', ' 102', ' 398', ' 127', '2'], ['90', '1', '366', ' 102', ' 398', ' 127', '2'], ['91', '1', '365', ' 103', ' 399', ' 128', '2'], ['92', '1', '365', ' 103', ' 399', ' 128', '2'], ['93', '1', '365', ' 104', ' 398', ' 129', '2'], ['94', '1', '365', ' 104', ' 399', ' 129', '2'], ['95', '1', '365', ' 104', ' 399', ' 130', '2'], ['96', '1', '366', ' 105', ' 399', ' 130', '2'], ['97', '1', '367', ' 105', ' 400', ' 131', '2'], ['98', '1', '368', ' 106', ' 399', ' 131', '2'], ['99', '1', '368', ' 106', ' 400', ' 131', '2'], ['100', '1', '369',

In [48]:
def json_to_json_array(file_path,violation_json):
    with open(file_path,'r') as f:
        contents=f.read()
    splitted_array=[i.split(',') for i in contents.split('\n')]
        
    main_arr=[]
    for i in violation_json:
        temp_json={}
        temp_json[f'{i}']=[]
        for j in splitted_array:
            if len(j) > 0 and len(j)>6:
                # print(j)
                if str(i)==str(j[1]):
                    temp_json[f'{i}'].append(j)
        main_arr.append(temp_json)
    return main_arr

In [43]:
print(len(main_arr[0]))
print(len(main_arr[1]))

1
1


In [44]:
len(main_arr)

28

In [45]:
main_arr

[{'1': [['77', '1', '364', ' 104', ' 394', ' 125', '2'],
   ['81', '1', '363', ' 103', ' 395', ' 125', '2'],
   ['82', '1', '364', ' 102', ' 396', ' 126', '2'],
   ['83', '1', '364', ' 102', ' 397', ' 126', '2'],
   ['84', '1', '364', ' 103', ' 397', ' 127', '2'],
   ['85', '1', '365', ' 103', ' 397', ' 127', '2'],
   ['86', '1', '365', ' 103', ' 397', ' 127', '2'],
   ['87', '1', '365', ' 103', ' 398', ' 127', '2'],
   ['88', '1', '365', ' 103', ' 398', ' 127', '2'],
   ['89', '1', '365', ' 102', ' 398', ' 127', '2'],
   ['90', '1', '366', ' 102', ' 398', ' 127', '2'],
   ['91', '1', '365', ' 103', ' 399', ' 128', '2'],
   ['92', '1', '365', ' 103', ' 399', ' 128', '2'],
   ['93', '1', '365', ' 104', ' 398', ' 129', '2'],
   ['94', '1', '365', ' 104', ' 399', ' 129', '2'],
   ['95', '1', '365', ' 104', ' 399', ' 130', '2'],
   ['96', '1', '366', ' 105', ' 399', ' 130', '2'],
   ['97', '1', '367', ' 105', ' 400', ' 131', '2'],
   ['98', '1', '368', ' 106', ' 399', ' 131', '2'],
   ['99

In [2]:
dummy_arr=[['2365', '56', '350', ' 107', ' 377', ' 131', '2'], ['2366', '56', '350', ' 108', ' 376', ' 131', '2'], ['2367', '56', '349', ' 107', ' 377', ' 131', '2'], ['2368', '56', '351', ' 109', ' 376', ' 132', '2'], ['2369', '56', '351', ' 111', ' 375', ' 132', '2'], ['2370', '56', '352', ' 112', ' 376', ' 133', '2'], ['2371', '56', '351', ' 110', ' 376', ' 133', '2'], ['2372', '56', '350', ' 110', ' 377', ' 133', '2'], ['2373', '56', '350', ' 110', ' 378', ' 134', '2'], ['2374', '56', '350', ' 110', ' 378', ' 135', '2'], ['2375', '56', '350', ' 110', ' 378', ' 135', '2'], ['2376', '56', '350', ' 110', ' 378', ' 135', '2'], ['2377', '56', '350', ' 110', ' 379', ' 136', '2'], ['2378', '56', '349', ' 110', ' 380', ' 137', '2'], ['2379', '56', '349', ' 110', ' 380', ' 138', '2'], ['2380', '56', '350', ' 110', ' 380', ' 139', '2'], ['2381', '56', '350', ' 112', ' 379', ' 139', '2'], ['2382', '56', '350', ' 112', ' 380', ' 140', '2'], ['2383', '56', '351', ' 113', ' 380', ' 141', '2'], ['2384', '56', '351', ' 115', ' 379', ' 141', '2'], ['2385', '56', '351', ' 115', ' 379', ' 141', '2'], ['2386', '56', '351', ' 116', ' 379', ' 142', '2'], ['2387', '56', '351', ' 117', ' 379', ' 143', '2'], ['2388', '56', '351', ' 117', ' 380', ' 143', '2'], ['2389', '56', '351', ' 117', ' 380', ' 144', '2'], ['2390', '56', '350', ' 117', ' 380', ' 145', '2'], ['2391', '56', '350', ' 117', ' 380', ' 146', '2'], ['2392', '56', '349', ' 117', ' 381', ' 146', '2'], ['2393', '56', '351', ' 121', ' 379', ' 147', '2']]

In [7]:
def arr_to_coordinate_json(arr):
    """
    Retrun a json with keys as frame numbers and values are coordinates for each and every frame 
    """
    main_json={}
    for i  in arr:
        coord_array=[]
        coord_array.append(i[2])
        coord_array.append(i[3])
        coord_array.append(i[4])
        coord_array.append(i[5])
        main_json[i[0]]=coord_array
    return main_json

In [6]:
print(main_json)

{'2365': ['350', ' 107', ' 377', ' 131'], '2366': ['350', ' 108', ' 376', ' 131'], '2367': ['349', ' 107', ' 377', ' 131'], '2368': ['351', ' 109', ' 376', ' 132'], '2369': ['351', ' 111', ' 375', ' 132'], '2370': ['352', ' 112', ' 376', ' 133'], '2371': ['351', ' 110', ' 376', ' 133'], '2372': ['350', ' 110', ' 377', ' 133'], '2373': ['350', ' 110', ' 378', ' 134'], '2374': ['350', ' 110', ' 378', ' 135'], '2375': ['350', ' 110', ' 378', ' 135'], '2376': ['350', ' 110', ' 378', ' 135'], '2377': ['350', ' 110', ' 379', ' 136'], '2378': ['349', ' 110', ' 380', ' 137'], '2379': ['349', ' 110', ' 380', ' 138'], '2380': ['350', ' 110', ' 380', ' 139'], '2381': ['350', ' 112', ' 379', ' 139'], '2382': ['350', ' 112', ' 380', ' 140'], '2383': ['351', ' 113', ' 380', ' 141'], '2384': ['351', ' 115', ' 379', ' 141'], '2385': ['351', ' 115', ' 379', ' 141'], '2386': ['351', ' 116', ' 379', ' 142'], '2387': ['351', ' 117', ' 379', ' 143'], '2388': ['351', ' 117', ' 380', ' 143'], '2389': ['351',

In [12]:
import os
demo_path='DMEOM/30_05_2024_all_frame_detection_detail.csv'
print(os.path.basename(demo_path).split('.')[0])

30_05_2024_all_frame_detection_detail


In [8]:
def json_arr_to_json(json_arr):
    main_json={}
    for json in json_arr:
        for key_ in json:
            main_json[key_]=json[key_]
    return main_json

In [13]:
main_json={}
for i in violation_coordinates_json:
    for j in i:
        main_json[j]=i[j]
        

In [14]:
print(main_json)

{'2': [['82', '2', '366', ' 103', ' 394', ' 125', '2'], ['83', '2', '366', ' 102', ' 395', ' 126', '2'], ['84', '2', '366', ' 103', ' 395', ' 127', '2'], ['85', '2', '367', ' 103', ' 395', ' 127', '2'], ['86', '2', '367', ' 104', ' 395', ' 127', '2'], ['87', '2', '367', ' 103', ' 396', ' 127', '2'], ['88', '2', '367', ' 103', ' 396', ' 127', '2'], ['89', '2', '367', ' 103', ' 396', ' 127', '2'], ['90', '2', '367', ' 103', ' 397', ' 127', '2'], ['91', '2', '367', ' 103', ' 398', ' 128', '2'], ['92', '2', '367', ' 103', ' 398', ' 128', '2'], ['93', '2', '366', ' 104', ' 398', ' 129', '2'], ['94', '2', '366', ' 104', ' 398', ' 130', '2'], ['95', '2', '367', ' 104', ' 399', ' 130', '2'], ['96', '2', '368', ' 105', ' 399', ' 130', '2'], ['97', '2', '368', ' 105', ' 399', ' 131', '2'], ['98', '2', '369', ' 106', ' 399', ' 131', '2'], ['99', '2', '369', ' 106', ' 400', ' 131', '2'], ['100', '2', '369', ' 107', ' 401', ' 132', '2'], ['101', '2', '370', ' 107', ' 401', ' 133', '2'], ['104', '2'

In [15]:
{'2': [['82', '2', '366', ' 103', ' 394', ' 125', '2'], ['83', '2', '366', ' 102', ' 395', ' 126', '2'], ['84', '2', '366', ' 103', ' 395', ' 127', '2'], ['85', '2', '367', ' 103', ' 395', ' 127', '2'], ['86', '2', '367', ' 104', ' 395', ' 127', '2'], ['87', '2', '367', ' 103', ' 396', ' 127', '2'], ['88', '2', '367', ' 103', ' 396', ' 127', '2'], ['89', '2', '367', ' 103', ' 396', ' 127', '2'], ['90', '2', '367', ' 103', ' 397', ' 127', '2'], ['91', '2', '367', ' 103', ' 398', ' 128', '2'], ['92', '2', '367', ' 103', ' 398', ' 128', '2'], ['93', '2', '366', ' 104', ' 398', ' 129', '2'], ['94', '2', '366', ' 104', ' 398', ' 130', '2'], ['95', '2', '367', ' 104', ' 399', ' 130', '2'], ['96', '2', '368', ' 105', ' 399', ' 130', '2'], ['97', '2', '368', ' 105', ' 399', ' 131', '2'], ['98', '2', '369', ' 106', ' 399', ' 131', '2'], ['99', '2', '369', ' 106', ' 400', ' 131', '2'], ['100', '2', '369', ' 107', ' 401', ' 132', '2'], ['101', '2', '370', ' 107', ' 401', ' 133', '2'], ['104', '2', '373', ' 110', ' 401', ' 133', '2'], ['105', '2', '374', ' 111', ' 401', ' 134', '2'], ['106', '2', '372', ' 110', ' 402', ' 134', '2'], ['107', '2', '372', ' 109', ' 403', ' 134', '2'], ['113', '2', '378', ' 118', ' 404', ' 138', '2'], ['114', '2', '379', ' 119', ' 404', ' 139', '2'], ['116', '2', '380', ' 118', ' 408', ' 140', '2'], ['117', '2', '381', ' 119', ' 408', ' 140', '2'], ['118', '2', '381', ' 120', ' 409', ' 141', '2'], ['119', '2', '380', ' 117', ' 410', ' 141', '2'], ['120', '2', '378', ' 113', ' 413', ' 140', '2'], ['121', '2', '379', ' 113', ' 413', ' 140', '2'], ['122', '2', '379', ' 114', ' 413', ' 141', '2'], ['124', '2', '379', ' 114', ' 414', ' 143', '2'], ['125', '2', '380', ' 114', ' 414', ' 144', '2'], ['128', '2', '382', ' 118', ' 414', ' 146', '2'], ['138', '2', '393', ' 128', ' 421', ' 151', '2'], ['141', '2', '394', ' 131', ' 423', ' 154', '2'], ['142', '2', '393', ' 131', ' 423', ' 155', '2'], ['143', '2', '393', ' 131', ' 424', ' 156', '2'], ['145', '2', '393', ' 132', ' 425', ' 157', '2'], ['146', '2', '395', ' 132', ' 427', ' 157', '2'], ['147', '2', '396', ' 133', ' 427', ' 156', '2'], ['148', '2', '396', ' 133', ' 428', ' 158', '2'], ['150', '2', '397', ' 135', ' 432', ' 161', '2'], ['151', '2', '397', ' 134', ' 434', ' 162', '2'], ['152', '2', '397', ' 135', ' 436', ' 164', '2'], ['153', '2', '398', ' 136', ' 437', ' 165', '2'], ['154', '2', '400', ' 137', ' 438', ' 166', '2'], ['155', '2', '402', ' 138', ' 441', ' 167', '2'], ['156', '2', '401', ' 138', ' 441', ' 167', '2'], ['157', '2', '401', ' 139', ' 442', ' 168', '2'], ['158', '2', '402', ' 140', ' 443', ' 169', '2'], ['159', '2', '401', ' 141', ' 442', ' 170', '2'], ['160', '2', '401', ' 141', ' 443', ' 171', '2'], ['161', '2', '401', ' 141', ' 444', ' 172', '2'], ['162', '2', '403', ' 143', ' 444', ' 173', '2'], ['163', '2', '404', ' 143', ' 445', ' 174', '2'], ['164', '2', '406', ' 144', ' 446', ' 174', '2'], ['165', '2', '407', ' 145', ' 447', ' 175', '2'], ['166', '2', '407', ' 146', ' 449', ' 178', '2'], ['167', '2', '407', ' 146', ' 451', ' 179', '2'], ['168', '2', '407', ' 146', ' 452', ' 180', '2'], ['169', '2', '409', ' 147', ' 454', ' 181', '2'], ['170', '2', '409', ' 148', ' 455', ' 183', '2'], ['171', '2', '411', ' 149', ' 456', ' 183', '2'], ['172', '2', '412', ' 148', ' 458', ' 184', '2'], ['173', '2', '413', ' 149', ' 460', ' 185', '2'], ['174', '2', '414', ' 150', ' 461', ' 186', '2'], ['175', '2', '415', ' 151', ' 462', ' 187', '2'], ['176', '2', '416', ' 152', ' 463', ' 188', '2'], ['177', '2', '417', ' 153', ' 464', ' 189', '2'], ['178', '2', '418', ' 153', ' 466', ' 191', '2'], ['179', '2', '419', ' 155', ' 468', ' 193', '2'], ['180', '2', '421', ' 157', ' 469', ' 194', '2'], ['181', '2', '422', ' 158', ' 471', ' 197', '2'], ['182', '2', '422', ' 159', ' 472', ' 198', '2'], ['183', '2', '423', ' 160', ' 475', ' 201', '2'], ['184', '2', '424', ' 161', ' 477', ' 203', '2'], ['185', '2', '425', ' 162', ' 478', ' 204', '2'], ['186', '2', '425', ' 163', ' 479', ' 206', '2'], ['187', '2', '427', ' 164', ' 480', ' 207', '2'], ['188', '2', '427', ' 165', ' 481', ' 208', '2'], ['189', '2', '429', ' 168', ' 482', ' 210', '2'], ['190', '2', '431', ' 169', ' 483', ' 211', '2'], ['191', '2', '432', ' 170', ' 486', ' 213', '2'], ['192', '2', '432', ' 171', ' 487', ' 215', '2'], ['193', '2', '433', ' 172', ' 490', ' 217', '2'], ['194', '2', '435', ' 173', ' 493', ' 219', '2'], ['195', '2', '435', ' 175', ' 495', ' 223', '2'], ['196', '2', '437', ' 177', ' 496', ' 224', '2'], ['197', '2', '439', ' 178', ' 498', ' 226', '2'], ['198', '2', '440', ' 179', ' 501', ' 229', '2'], ['199', '2', '442', ' 181', ' 504', ' 231', '2'], ['200', '2', '442', ' 183', ' 506', ' 235', '2'], ['201', '2', '444', ' 185', ' 508', ' 237', '2'], ['202', '2', '446', ' 186', ' 511', ' 239', '2'], ['203', '2', '446', ' 188', ' 512', ' 242', '2'], ['204', '2', '449', ' 192', ' 514', ' 245', '2'], ['205', '2', '450', ' 193', ' 518', ' 248', '2'], ['206', '2', '452', ' 195', ' 520', ' 250', '2'], ['207', '2', '453', ' 197', ' 523', ' 254', '2'], ['208', '2', '454', ' 199', ' 526', ' 258', '2'], ['209', '2', '456', ' 201', ' 530', ' 261', '2'], ['210', '2', '457', ' 202', ' 532', ' 263', '2'], ['211', '2', '458', ' 203', ' 535', ' 266', '2'], ['212', '2', '458', ' 203', ' 539', ' 271', '2'], ['213', '2', '462', ' 208', ' 541', ' 274', '2'], ['214', '2', '465', ' 212', ' 544', ' 278', '2'], ['215', '2', '466', ' 215', ' 548', ' 283', '2'], ['216', '2', '467', ' 216', ' 552', ' 287', '2'], ['217', '2', '470', ' 219', ' 555', ' 291', '2'], ['218', '2', '472', ' 222', ' 560', ' 296', '2'], ['219', '2', '475', ' 225', ' 563', ' 299', '2'], ['220', '2', '475', ' 227', ' 567', ' 305', '2'], ['221', '2', '478', ' 231', ' 572', ' 310', '2'], ['222', '2', '481', ' 234', ' 576', ' 314', '2'], ['223', '2', '484', ' 237', ' 581', ' 320', '2'], ['224', '2', '488', ' 241', ' 587', ' 324', '2'], ['225', '2', '491', ' 245', ' 593', ' 331', '2'], ['226', '2', '493', ' 248', ' 598', ' 337', '2'], ['227', '2', '496', ' 252', ' 604', ' 344', '2'], ['228', '2', '500', ' 256', ' 610', ' 350', '2'], ['229', '2', '502', ' 261', ' 616', ' 358', '2'], ['230', '2', '506', ' 267', ' 621', ' 364', '2'], ['231', '2', '510', ' 271', ' 629', ' 373', '2'], ['232', '2', '515', ' 276', ' 638', ' 381', '2'], ['233', '2', '519', ' 279', ' 646', ' 389', '2'], ['234', '2', '521', ' 284', ' 655', ' 400', '2'], ['235', '2', '526', ' 291', ' 662', ' 409', '2'], ['236', '2', '534', ' 297', ' 668', ' 413', '2'], ['237', '2', '543', ' 305', ' 671', ' 414', '2'], ['238', '2', '551', ' 312', ' 676', ' 416', '2'], ['239', '2', '560', ' 319', ' 680', ' 416', '2'], ['240', '2', '570', ' 323', ' 686', ' 414', '2'], ['241', '2', '577', ' 331', ' 687', ' 414', '2'], ['242', '2', '591', ' 341', ' 695', ' 414', '2'], ['243', '2', '603', ' 350', ' 701', ' 413', '2'], ['244', '2', '612', ' 360', ' 700', ' 413', '2']], '7': [['161', '7', '370', ' 118', ' 396', ' 140', '2'], ['162', '7', '370', ' 117', ' 397', ' 140', '2'], ['163', '7', '369', ' 117', ' 397', ' 141', '2'], ['164', '7', '368', ' 117', ' 398', ' 142', '2'], ['165', '7', '369', ' 117', ' 399', ' 143', '2'], ['166', '7', '370', ' 118', ' 399', ' 143', '2'], ['167', '7', '368', ' 116', ' 400', ' 144', '2'], ['170', '7', '369', ' 117', ' 401', ' 146', '2'], ['171', '7', '369', ' 118', ' 401', ' 146', '2'], ['172', '7', '370', ' 119', ' 401', ' 146', '2'], ['176', '7', '370', ' 121', ' 402', ' 150', '2'], ['177', '7', '371', ' 123', ' 402', ' 151', '2'], ['178', '7', '371', ' 123', ' 403', ' 151', '2'], ['179', '7', '372', ' 124', ' 404', ' 152', '2'], ['180', '7', '372', ' 125', ' 403', ' 153', '2'], ['182', '7', '373', ' 126', ' 404', ' 154', '2'], ['183', '7', '374', ' 127', ' 406', ' 155', '2'], ['184', '7', '374', ' 128', ' 406', ' 156', '2'], ['185', '7', '375', ' 128', ' 407', ' 157', '2'], ['186', '7', '374', ' 128', ' 407', ' 158', '2'], ['187', '7', '374', ' 128', ' 408', ' 158', '2'], ['188', '7', '374', ' 129', ' 408', ' 160', '2'], ['189', '7', '374', ' 130', ' 409', ' 161', '2'], ['190', '7', '375', ' 131', ' 409', ' 162', '2'], ['191', '7', '375', ' 131', ' 411', ' 164', '2'], ['192', '7', '375', ' 130', ' 412', ' 165', '2'], ['193', '7', '376', ' 131', ' 413', ' 165', '2'], ['194', '7', '376', ' 131', ' 415', ' 166', '2'], ['195', '7', '376', ' 132', ' 414', ' 168', '2'], ['196', '7', '377', ' 134', ' 415', ' 169', '2'], ['197', '7', '378', ' 135', ' 415', ' 170', '2'], ['198', '7', '378', ' 134', ' 417', ' 171', '2'], ['199', '7', '380', ' 137', ' 418', ' 173', '2'], ['200', '7', '380', ' 137', ' 419', ' 174', '2'], ['201', '7', '382', ' 138', ' 420', ' 175', '2'], ['202', '7', '383', ' 138', ' 423', ' 176', '2'], ['203', '7', '383', ' 140', ' 423', ' 177', '2'], ['204', '7', '385', ' 142', ' 423', ' 179', '2'], ['205', '7', '386', ' 143', ' 424', ' 180', '2'], ['207', '7', '387', ' 145', ' 427', ' 182', '2'], ['209', '7', '389', ' 145', ' 432', ' 186', '2'], ['210', '7', '389', ' 145', ' 432', ' 187', '2'], ['211', '7', '390', ' 147', ' 435', ' 189', '2'], ['212', '7', '392', ' 148', ' 435', ' 190', '2'], ['213', '7', '392', ' 147', ' 437', ' 191', '2'], ['214', '7', '393', ' 149', ' 439', ' 193', '2'], ['215', '7', '393', ' 151', ' 441', ' 196', '2'], ['216', '7', '394', ' 151', ' 443', ' 197', '2'], ['217', '7', '393', ' 151', ' 445', ' 200', '2'], ['218', '7', '396', ' 155', ' 446', ' 202', '2'], ['219', '7', '397', ' 157', ' 448', ' 204', '2'], ['220', '7', '398', ' 157', ' 451', ' 205', '2'], ['221', '7', '400', ' 159', ' 453', ' 208', '2'], ['222', '7', '401', ' 159', ' 455', ' 209', '2'], ['223', '7', '400', ' 159', ' 457', ' 212', '2'], ['224', '7', '401', ' 161', ' 458', ' 214', '2'], ['225', '7', '402', ' 161', ' 461', ' 217', '2'], ['226', '7', '402', ' 162', ' 463', ' 219', '2'], ['227', '7', '404', ' 163', ' 466', ' 221', '2'], ['228', '7', '407', ' 166', ' 468', ' 224', '2'], ['229', '7', '408', ' 168', ' 470', ' 227', '2'], ['230', '7', '409', ' 168', ' 473', ' 229', '2'], ['231', '7', '411', ' 170', ' 475', ' 231', '2'], ['232', '7', '411', ' 169', ' 480', ' 235', '2'], ['233', '7', '413', ' 171', ' 482', ' 237', '2'], ['234', '7', '415', ' 173', ' 485', ' 240', '2'], ['235', '7', '417', ' 174', ' 487', ' 243', '2'], ['236', '7', '420', ' 181', ' 489', ' 248', '2'], ['237', '7', '422', ' 185', ' 491', ' 251', '2'], ['238', '7', '423', ' 183', ' 496', ' 254', '2'], ['239', '7', '425', ' 184', ' 499', ' 257', '2'], ['240', '7', '428', ' 189', ' 502', ' 261', '2'], ['241', '7', '430', ' 191', ' 506', ' 265', '2'], ['242', '7', '432', ' 192', ' 511', ' 269', '2'], ['243', '7', '433', ' 194', ' 515', ' 274', '2'], ['244', '7', '435', ' 196', ' 518', ' 277', '2'], ['245', '7', '438', ' 198', ' 523', ' 280', '2'], ['246', '7', '440', ' 199', ' 528', ' 286', '2'], ['247', '7', '442', ' 201', ' 533', ' 290', '2'], ['248', '7', '445', ' 204', ' 538', ' 295', '2'], ['249', '7', '448', ' 207', ' 542', ' 300', '2'], ['250', '7', '451', ' 211', ' 546', ' 305', '2'], ['251', '7', '453', ' 215', ' 552', ' 311', '2'], ['252', '7', '455', ' 217', ' 558', ' 319', '2'], ['253', '7', '458', ' 220', ' 564', ' 324', '2'], ['254', '7', '462', ' 223', ' 570', ' 330', '2'], ['255', '7', '466', ' 226', ' 578', ' 336', '2'], ['256', '7', '470', ' 231', ' 584', ' 344', '2'], ['257', '7', '474', ' 236', ' 590', ' 351', '2'], ['258', '7', '478', ' 240', ' 598', ' 358', '2'], ['259', '7', '482', ' 243', ' 608', ' 367', '2'], ['260', '7', '485', ' 247', ' 616', ' 376', '2'], ['261', '7', '489', ' 251', ' 626', ' 386', '2'], ['262', '7', '495', ' 257', ' 636', ' 396', '2'], ['263', '7', '501', ' 264', ' 645', ' 407', '2'], ['264', '7', '510', ' 271', ' 653', ' 412', '2'], ['265', '7', '518', ' 275', ' 660', ' 414', '2'], ['266', '7', '528', ' 280', ' 670', ' 415', '2'], ['267', '7', '541', ' 286', ' 681', ' 416', '2'], ['268', '7', '557', ' 293', ' 696', ' 416', '2'], ['271', '7', '576', ' 313', ' 698', ' 415', '2'], ['272', '7', '588', ' 324', ' 703', ' 415', '2'], ['273', '7', '600', ' 334', ' 708', ' 413', '2'], ['274', '7', '612', ' 344', ' 713', ' 413', '2'], ['275', '7', '627', ' 355', ' 719', ' 413', '2']], '40': [['1475', '40', '347', ' 114', ' 368', ' 132', '2'], ['1476', '40', '348', ' 114', ' 370', ' 133', '2'], ['1477', '40', '348', ' 114', ' 370', ' 133', '2'], ['1478', '40', '348', ' 114', ' 370', ' 134', '2'], ['1479', '40', '347', ' 114', ' 370', ' 134', '2'], ['1480', '40', '347', ' 114', ' 370', ' 134', '2'], ['1481', '40', '347', ' 115', ' 370', ' 135', '2'], ['1482', '40', '347', ' 116', ' 370', ' 135', '2'], ['1483', '40', '347', ' 116', ' 371', ' 136', '2'], ['1484', '40', '347', ' 116', ' 371', ' 136', '2'], ['1485', '40', '347', ' 116', ' 372', ' 137', '2'], ['1486', '40', '347', ' 117', ' 372', ' 137', '2'], ['1487', '40', '348', ' 119', ' 372', ' 138', '2'], ['1488', '40', '347', ' 119', ' 373', ' 140', '2'], ['1489', '40', '347', ' 119', ' 374', ' 140', '2'], ['1491', '40', '347', ' 120', ' 374', ' 142', '2'], ['1492', '40', '348', ' 121', ' 375', ' 143', '2'], ['1493', '40', '346', ' 120', ' 375', ' 144', '2'], ['1494', '40', '346', ' 121', ' 375', ' 145', '2'], ['1495', '40', '347', ' 121', ' 375', ' 145', '2'], ['1496', '40', '348', ' 123', ' 375', ' 146', '2'], ['1497', '40', '348', ' 124', ' 375', ' 146', '2'], ['1498', '40', '349', ' 126', ' 375', ' 147', '2'], ['1499', '40', '350', ' 128', ' 375', ' 148', '2'], ['1500', '40', '349', ' 127', ' 377', ' 148', '2'], ['1501', '40', '349', ' 127', ' 377', ' 148', '2'], ['1502', '40', '348', ' 127', ' 378', ' 150', '2'], ['1503', '40', '348', ' 127', ' 378', ' 150', '2'], ['1504', '40', '347', ' 127', ' 379', ' 151', '2'], ['1505', '40', '347', ' 126', ' 380', ' 152', '2'], ['1506', '40', '347', ' 127', ' 380', ' 153', '2'], ['1507', '40', '346', ' 128', ' 380', ' 153', '2'], ['1508', '40', '347', ' 129', ' 380', ' 154', '2'], ['1509', '40', '348', ' 129', ' 380', ' 155', '2'], ['1510', '40', '348', ' 130', ' 381', ' 155', '2'], ['1511', '40', '348', ' 129', ' 383', ' 156', '2'], ['1512', '40', '349', ' 130', ' 384', ' 157', '2'], ['1513', '40', '348', ' 131', ' 383', ' 158', '2'], ['1514', '40', '348', ' 131', ' 384', ' 159', '2'], ['1515', '40', '348', ' 132', ' 385', ' 162', '2'], ['1516', '40', '348', ' 133', ' 386', ' 163', '2'], ['1517', '40', '349', ' 133', ' 388', ' 164', '2'], ['1518', '40', '348', ' 134', ' 388', ' 166', '2'], ['1519', '40', '348', ' 135', ' 389', ' 167', '2'], ['1520', '40', '346', ' 135', ' 388', ' 168', '2'], ['1521', '40', '346', ' 135', ' 388', ' 169', '2'], ['1522', '40', '347', ' 135', ' 388', ' 169', '2'], ['1523', '40', '346', ' 135', ' 389', ' 170', '2'], ['1524', '40', '347', ' 136', ' 389', ' 171', '2'], ['1525', '40', '346', ' 135', ' 391', ' 173', '2'], ['1526', '40', '348', ' 137', ' 391', ' 175', '2'], ['1527', '40', '348', ' 138', ' 392', ' 176', '2'], ['1528', '40', '348', ' 140', ' 392', ' 178', '2'], ['1529', '40', '349', ' 141', ' 393', ' 180', '2'], ['1530', '40', '349', ' 143', ' 393', ' 181', '2'], ['1531', '40', '349', ' 144', ' 392', ' 183', '2'], ['1532', '40', '349', ' 146', ' 393', ' 184', '2'], ['1533', '40', '349', ' 146', ' 394', ' 186', '2'], ['1534', '40', '350', ' 149', ' 394', ' 187', '2'], ['1535', '40', '351', ' 150', ' 395', ' 188', '2'], ['1536', '40', '352', ' 151', ' 396', ' 190', '2'], ['1537', '40', '353', ' 153', ' 398', ' 193', '2'], ['1538', '40', '354', ' 155', ' 399', ' 195', '2'], ['1539', '40', '354', ' 157', ' 400', ' 197', '2'], ['1540', '40', '353', ' 156', ' 401', ' 199', '2'], ['1541', '40', '354', ' 157', ' 401', ' 200', '2'], ['1542', '40', '352', ' 156', ' 402', ' 202', '2'], ['1543', '40', '353', ' 159', ' 402', ' 204', '2'], ['1544', '40', '353', ' 160', ' 403', ' 206', '2'], ['1545', '40', '352', ' 160', ' 405', ' 209', '2'], ['1546', '40', '353', ' 162', ' 405', ' 211', '2'], ['1547', '40', '352', ' 164', ' 406', ' 214', '2'], ['1548', '40', '353', ' 165', ' 408', ' 216', '2'], ['1549', '40', '353', ' 166', ' 410', ' 220', '2'], ['1550', '40', '354', ' 168', ' 411', ' 223', '2'], ['1551', '40', '354', ' 170', ' 412', ' 225', '2'], ['1552', '40', '354', ' 171', ' 413', ' 228', '2'], ['1553', '40', '356', ' 173', ' 416', ' 231', '2'], ['1554', '40', '356', ' 175', ' 418', ' 235', '2'], ['1555', '40', '356', ' 177', ' 420', ' 238', '2'], ['1556', '40', '356', ' 177', ' 422', ' 242', '2'], ['1557', '40', '356', ' 180', ' 424', ' 247', '2'], ['1558', '40', '357', ' 182', ' 426', ' 250', '2'], ['1559', '40', '359', ' 186', ' 426', ' 252', '2'], ['1560', '40', '359', ' 188', ' 429', ' 257', '2'], ['1561', '40', '360', ' 192', ' 431', ' 262', '2'], ['1562', '40', '360', ' 193', ' 433', ' 265', '2'], ['1563', '40', '360', ' 196', ' 436', ' 272', '2'], ['1564', '40', '360', ' 198', ' 438', ' 276', '2'], ['1565', '40', '362', ' 201', ' 441', ' 279', '2'], ['1566', '40', '364', ' 204', ' 444', ' 284', '2'], ['1567', '40', '368', ' 214', ' 444', ' 288', '2'], ['1568', '40', '365', ' 212', ' 449', ' 296', '2'], ['1569', '40', '365', ' 216', ' 450', ' 300', '2'], ['1570', '40', '366', ' 219', ' 455', ' 307', '2'], ['1571', '40', '368', ' 222', ' 459', ' 312', '2'], ['1572', '40', '368', ' 226', ' 463', ' 321', '2'], ['1573', '40', '369', ' 230', ' 465', ' 326', '2'], ['1574', '40', '369', ' 234', ' 470', ' 335', '2'], ['1575', '40', '370', ' 240', ' 475', ' 345', '2'], ['1576', '40', '370', ' 244', ' 479', ' 352', '2'], ['1577', '40', '371', ' 249', ' 484', ' 361', '2'], ['1578', '40', '372', ' 254', ' 490', ' 372', '2'], ['1579', '40', '373', ' 260', ' 497', ' 384', '2'], ['1580', '40', '373', ' 266', ' 505', ' 399', '2'], ['1581', '40', '375', ' 272', ' 509', ' 408', '2'], ['1582', '40', '380', ' 279', ' 513', ' 413', '2'], ['1583', '40', '385', ' 285', ' 516', ' 415', '2'], ['1584', '40', '392', ' 293', ' 520', ' 417', '2'], ['1585', '40', '400', ' 301', ' 515', ' 410', '2'], ['1586', '40', '407', ' 309', ' 519', ' 411', '2'], ['1587', '40', '414', ' 318', ' 523', ' 414', '2'], ['1588', '40', '415', ' 325', ' 520', ' 413', '2'], ['1589', '40', '422', ' 338', ' 516', ' 413', '2'], ['1590', '40', '430', ' 350', ' 515', ' 412', '2']], '56': [['2362', '56', '350', ' 106', ' 375', ' 128', '2'], ['2363', '56', '350', ' 106', ' 375', ' 129', '2'], ['2365', '56', '350', ' 107', ' 375', ' 130', '2'], ['2369', '56', '352', ' 110', ' 374', ' 131', '2'], ['2372', '56', '352', ' 111', ' 375', ' 132', '2'], ['2373', '56', '351', ' 110', ' 377', ' 133', '2'], ['2374', '56', '351', ' 110', ' 377', ' 134', '2'], ['2375', '56', '351', ' 111', ' 377', ' 135', '2'], ['2376', '56', '351', ' 110', ' 377', ' 135', '2'], ['2377', '56', '350', ' 110', ' 378', ' 136', '2'], ['2378', '56', '350', ' 110', ' 379', ' 137', '2'], ['2379', '56', '349', ' 110', ' 379', ' 138', '2'], ['2380', '56', '350', ' 110', ' 379', ' 139', '2'], ['2381', '56', '350', ' 112', ' 378', ' 139', '2'], ['2382', '56', '350', ' 112', ' 379', ' 140', '2'], ['2383', '56', '351', ' 112', ' 379', ' 141', '2'], ['2386', '56', '352', ' 116', ' 378', ' 142', '2'], ['2387', '56', '352', ' 117', ' 378', ' 143', '2'], ['2388', '56', '351', ' 117', ' 379', ' 144', '2'], ['2389', '56', '351', ' 117', ' 379', ' 144', '2'], ['2390', '56', '351', ' 117', ' 379', ' 145', '2'], ['2391', '56', '350', ' 117', ' 380', ' 145', '2'], ['2392', '56', '350', ' 117', ' 380', ' 146', '2'], ['2393', '56', '352', ' 123', ' 378', ' 147', '2'], ['2394', '56', '350', ' 120', ' 379', ' 147', '2'], ['2397', '56', '353', ' 126', ' 379', ' 149', '2'], ['2398', '56', '351', ' 124', ' 380', ' 150', '2'], ['2399', '56', '352', ' 125', ' 381', ' 151', '2'], ['2401', '56', '351', ' 124', ' 382', ' 153', '2'], ['2402', '56', '351', ' 126', ' 382', ' 153', '2'], ['2403', '56', '351', ' 126', ' 382', ' 154', '2'], ['2404', '56', '351', ' 126', ' 383', ' 155', '2'], ['2407', '56', '351', ' 128', ' 384', ' 158', '2'], ['2409', '56', '350', ' 129', ' 386', ' 160', '2'], ['2410', '56', '350', ' 129', ' 387', ' 162', '2'], ['2411', '56', '350', ' 130', ' 388', ' 164', '2'], ['2412', '56', '350', ' 131', ' 388', ' 165', '2'], ['2413', '56', '349', ' 131', ' 389', ' 168', '2'], ['2415', '56', '349', ' 133', ' 389', ' 171', '2'], ['2417', '56', '349', ' 134', ' 390', ' 172', '2'], ['2418', '56', '349', ' 135', ' 390', ' 174', '2'], ['2419', '56', '349', ' 136', ' 390', ' 176', '2'], ['2421', '56', '349', ' 137', ' 390', ' 177', '2'], ['2422', '56', '350', ' 138', ' 391', ' 179', '2'], ['2423', '56', '350', ' 140', ' 392', ' 181', '2'], ['2424', '56', '349', ' 139', ' 394', ' 183', '2'], ['2425', '56', '349', ' 140', ' 393', ' 185', '2'], ['2426', '56', '349', ' 140', ' 394', ' 186', '2'], ['2427', '56', '349', ' 141', ' 395', ' 188', '2'], ['2428', '56', '350', ' 143', ' 396', ' 190', '2'], ['2430', '56', '351', ' 146', ' 397', ' 193', '2'], ['2432', '56', '351', ' 149', ' 398', ' 197', '2'], ['2433', '56', '351', ' 150', ' 399', ' 199', '2'], ['2434', '56', '352', ' 151', ' 401', ' 202', '2'], ['2435', '56', '352', ' 152', ' 402', ' 204', '2'], ['2436', '56', '351', ' 153', ' 402', ' 206', '2'], ['2437', '56', '351', ' 154', ' 402', ' 209', '2'], ['2438', '56', '352', ' 156', ' 403', ' 211', '2'], ['2439', '56', '352', ' 158', ' 404', ' 214', '2'], ['2440', '56', '352', ' 160', ' 404', ' 217', '2'], ['2442', '56', '352', ' 161', ' 407', ' 221', '2'], ['2443', '56', '352', ' 163', ' 408', ' 225', '2'], ['2446', '56', '351', ' 167', ' 411', ' 233', '2'], ['2447', '56', '352', ' 170', ' 413', ' 237', '2'], ['2448', '56', '355', ' 178', ' 413', ' 241', '2'], ['2449', '56', '356', ' 181', ' 416', ' 247', '2'], ['2450', '56', '356', ' 182', ' 418', ' 250', '2'], ['2451', '56', '355', ' 182', ' 421', ' 252', '2'], ['2452', '56', '355', ' 186', ' 423', ' 258', '2'], ['2453', '56', '356', ' 190', ' 425', ' 262', '2'], ['2454', '56', '353', ' 190', ' 426', ' 267', '2'], ['2455', '56', '354', ' 200', ' 424', ' 273', '2'], ['2456', '56', '357', ' 207', ' 425', ' 277', '2'], ['2457', '56', '355', ' 203', ' 429', ' 279', '2'], ['2458', '56', '353', ' 201', ' 435', ' 284', '2'], ['2459', '56', '352', ' 201', ' 438', ' 289', '2'], ['2460', '56', '351', ' 205', ' 442', ' 297', '2'], ['2461', '56', '352', ' 207', ' 443', ' 300', '2'], ['2462', '56', '352', ' 211', ' 447', ' 309', '2'], ['2463', '56', '353', ' 217', ' 449', ' 316', '2'], ['2464', '56', '354', ' 219', ' 454', ' 323', '2'], ['2465', '56', '360', ' 235', ' 452', ' 330', '2'], ['2466', '56', '356', ' 231', ' 461', ' 339', '2'], ['2468', '56', '356', ' 239', ' 468', ' 354', '2'], ['2469', '56', '353', ' 243', ' 473', ' 367', '2'], ['2471', '56', '351', ' 253', ' 481', ' 387', '2'], ['2472', '56', '351', ' 259', ' 489', ' 403', '2'], ['2473', '56', '353', ' 266', ' 492', ' 411', '2'], ['2474', '56', '357', ' 272', ' 495', ' 414', '2'], ['2475', '56', '363', ' 278', ' 499', ' 417', '2'], ['2479', '56', '381', ' 301', ' 496', ' 415', '2'], ['2480', '56', '390', ' 318', ' 492', ' 415', '2']], '58': [['2798', '58', '354', ' 130', ' 375', ' 148', '2'], ['2802', '58', '355', ' 131', ' 381', ' 152', '2'], ['2805', '58', '354', ' 128', ' 386', ' 154', '2'], ['2806', '58', '354', ' 129', ' 387', ' 156', '2'], ['2808', '58', '351', ' 126', ' 389', ' 158', '2'], ['2810', '58', '352', ' 127', ' 390', ' 160', '2'], ['2811', '58', '353', ' 129', ' 391', ' 161', '2'], ['2812', '58', '354', ' 133', ' 390', ' 163', '2'], ['2813', '58', '356', ' 133', ' 393', ' 165', '2'], ['2814', '58', '356', ' 132', ' 395', ' 165', '2'], ['2815', '58', '355', ' 131', ' 396', ' 167', '2'], ['2816', '58', '356', ' 131', ' 399', ' 168', '2'], ['2817', '58', '355', ' 130', ' 400', ' 170', '2'], ['2818', '58', '356', ' 134', ' 399', ' 171', '2'], ['2819', '58', '356', ' 134', ' 399', ' 172', '2'], ['2820', '58', '357', ' 135', ' 399', ' 173', '2'], ['2821', '58', '359', ' 138', ' 399', ' 174', '2'], ['2822', '58', '359', ' 137', ' 400', ' 175', '2'], ['2823', '58', '360', ' 138', ' 401', ' 176', '2'], ['2824', '58', '361', ' 142', ' 401', ' 179', '2'], ['2825', '58', '363', ' 145', ' 401', ' 180', '2'], ['2826', '58', '362', ' 143', ' 403', ' 182', '2'], ['2827', '58', '362', ' 144', ' 404', ' 183', '2'], ['2828', '58', '363', ' 144', ' 406', ' 185', '2'], ['2829', '58', '363', ' 144', ' 408', ' 187', '2'], ['2830', '58', '365', ' 146', ' 409', ' 189', '2'], ['2831', '58', '366', ' 148', ' 410', ' 190', '2'], ['2832', '58', '368', ' 150', ' 411', ' 192', '2'], ['2833', '58', '367', ' 149', ' 413', ' 193', '2'], ['2834', '58', '367', ' 150', ' 414', ' 196', '2'], ['2835', '58', '368', ' 152', ' 414', ' 198', '2'], ['2836', '58', '370', ' 154', ' 415', ' 199', '2'], ['2837', '58', '370', ' 154', ' 417', ' 201', '2'], ['2838', '58', '371', ' 157', ' 418', ' 204', '2'], ['2839', '58', '372', ' 160', ' 420', ' 207', '2'], ['2840', '58', '375', ' 163', ' 421', ' 209', '2'], ['2841', '58', '374', ' 162', ' 423', ' 211', '2'], ['2842', '58', '375', ' 164', ' 425', ' 213', '2'], ['2843', '58', '375', ' 164', ' 428', ' 216', '2'], ['2844', '58', '374', ' 162', ' 432', ' 220', '2'], ['2845', '58', '377', ' 167', ' 433', ' 222', '2'], ['2846', '58', '379', ' 170', ' 434', ' 226', '2'], ['2847', '58', '379', ' 172', ' 435', ' 228', '2'], ['2848', '58', '382', ' 177', ' 437', ' 231', '2'], ['2849', '58', '384', ' 179', ' 440', ' 234', '2'], ['2850', '58', '385', ' 180', ' 443', ' 237', '2'], ['2851', '58', '385', ' 183', ' 444', ' 240', '2'], ['2852', '58', '387', ' 185', ' 448', ' 244', '2'], ['2853', '58', '385', ' 180', ' 455', ' 249', '2'], ['2854', '58', '388', ' 186', ' 457', ' 253', '2'], ['2855', '58', '388', ' 183', ' 461', ' 256', '2'], ['2856', '58', '393', ' 193', ' 461', ' 260', '2'], ['2857', '58', '391', ' 189', ' 467', ' 265', '2'], ['2858', '58', '393', ' 193', ' 470', ' 270', '2'], ['2859', '58', '397', ' 202', ' 471', ' 275', '2'], ['2860', '58', '400', ' 207', ' 475', ' 280', '2'], ['2861', '58', '399', ' 203', ' 483', ' 286', '2'], ['2862', '58', '398', ' 199', ' 489', ' 290', '2'], ['2863', '58', '399', ' 201', ' 493', ' 296', '2'], ['2864', '58', '401', ' 203', ' 499', ' 301', '2'], ['2865', '58', '403', ' 206', ' 503', ' 308', '2'], ['2866', '58', '407', ' 210', ' 508', ' 314', '2'], ['2867', '58', '409', ' 214', ' 514', ' 322', '2'], ['2868', '58', '413', ' 218', ' 520', ' 329', '2'], ['2869', '58', '416', ' 221', ' 526', ' 335', '2'], ['2870', '58', '419', ' 224', ' 532', ' 343', '2'], ['2871', '58', '423', ' 231', ' 538', ' 351', '2'], ['2872', '58', '428', ' 238', ' 545', ' 360', '2'], ['2873', '58', '430', ' 242', ' 554', ' 372', '2'], ['2874', '58', '434', ' 247', ' 563', ' 382', '2'], ['2875', '58', '436', ' 252', ' 575', ' 400', '2'], ['2876', '58', '442', ' 258', ' 584', ' 409', '2'], ['2877', '58', '450', ' 266', ' 589', ' 413', '2'], ['2878', '58', '459', ' 273', ' 596', ' 415', '2'], ['2879', '58', '468', ' 279', ' 605', ' 418', '2'], ['2880', '58', '482', ' 289', ' 612', ' 416', '2'], ['3094', '58', '585', ' 239', ' 632', ' 285', '3'], ['3096', '58', '588', ' 232', ' 636', ' 280', '3'], ['3099', '58', '602', ' 244', ' 645', ' 288', '3'], ['3101', '58', '612', ' 257', ' 652', ' 297', '3'], ['3102', '58', '616', ' 261', ' 657', ' 303', '3'], ['3103', '58', '620', ' 263', ' 664', ' 308', '3'], ['3104', '58', '624', ' 267', ' 669', ' 314', '3'], ['3106', '58', '632', ' 274', ' 676', ' 320', '3']], '84': [['3591', '84', '343', ' 110', ' 366', ' 128', '2'], ['3596', '84', '342', ' 112', ' 366', ' 130', '2'], ['3597', '84', '343', ' 113', ' 366', ' 131', '2'], ['3598', '84', '343', ' 114', ' 366', ' 131', '2'], ['3599', '84', '343', ' 113', ' 367', ' 131', '2'], ['3600', '84', '343', ' 113', ' 368', ' 132', '2'], ['3601', '84', '343', ' 113', ' 368', ' 132', '2'], ['3602', '84', '344', ' 114', ' 368', ' 133', '2'], ['3603', '84', '344', ' 115', ' 368', ' 134', '2'], ['3604', '84', '344', ' 116', ' 368', ' 134', '2'], ['3605', '84', '344', ' 117', ' 368', ' 134', '2'], ['3606', '84', '345', ' 118', ' 368', ' 135', '2'], ['3607', '84', '345', ' 118', ' 369', ' 136', '2'], ['3608', '84', '344', ' 119', ' 369', ' 137', '2'], ['3609', '84', '344', ' 119', ' 369', ' 137', '2'], ['3610', '84', '344', ' 119', ' 369', ' 138', '2'], ['3611', '84', '344', ' 120', ' 370', ' 139', '2'], ['3612', '84', '344', ' 122', ' 370', ' 140', '2'], ['3613', '84', '345', ' 123', ' 370', ' 141', '2'], ['3614', '84', '345', ' 123', ' 371', ' 142', '2'], ['3615', '84', '344', ' 122', ' 371', ' 142', '2'], ['3616', '84', '344', ' 123', ' 372', ' 143', '2'], ['3617', '84', '344', ' 123', ' 372', ' 144', '2'], ['3618', '84', '344', ' 125', ' 371', ' 145', '2'], ['3619', '84', '344', ' 126', ' 371', ' 146', '2'], ['3620', '84', '343', ' 126', ' 372', ' 147', '2'], ['3621', '84', '344', ' 127', ' 372', ' 147', '2'], ['3622', '84', '344', ' 128', ' 372', ' 147', '2'], ['3623', '84', '344', ' 128', ' 373', ' 148', '2'], ['3624', '84', '344', ' 128', ' 373', ' 148', '2'], ['3625', '84', '343', ' 128', ' 374', ' 149', '2'], ['3626', '84', '342', ' 128', ' 374', ' 150', '2'], ['3627', '84', '342', ' 128', ' 374', ' 151', '2'], ['3628', '84', '342', ' 128', ' 376', ' 152', '2'], ['3629', '84', '341', ' 128', ' 376', ' 153', '2'], ['3630', '84', '342', ' 128', ' 376', ' 154', '2'], ['3631', '84', '342', ' 129', ' 376', ' 154', '2'], ['3632', '84', '342', ' 130', ' 375', ' 155', '2'], ['3633', '84', '342', ' 131', ' 376', ' 155', '2'], ['3634', '84', '342', ' 131', ' 376', ' 156', '2'], ['3635', '84', '342', ' 131', ' 376', ' 157', '2'], ['3636', '84', '342', ' 132', ' 377', ' 158', '2'], ['3637', '84', '342', ' 133', ' 378', ' 160', '2'], ['3638', '84', '343', ' 135', ' 378', ' 161', '2'], ['3639', '84', '342', ' 135', ' 379', ' 163', '2'], ['3640', '84', '343', ' 136', ' 379', ' 164', '2'], ['3641', '84', '343', ' 137', ' 379', ' 165', '2'], ['3642', '84', '342', ' 138', ' 380', ' 166', '2'], ['3643', '84', '341', ' 139', ' 378', ' 167', '2'], ['3644', '84', '342', ' 140', ' 379', ' 169', '2'], ['3645', '84', '341', ' 141', ' 379', ' 170', '2'], ['3646', '84', '341', ' 142', ' 380', ' 171', '2'], ['3647', '84', '341', ' 142', ' 381', ' 173', '2'], ['3648', '84', '342', ' 142', ' 382', ' 173', '2'], ['3649', '84', '342', ' 144', ' 382', ' 175', '2'], ['3650', '84', '343', ' 145', ' 383', ' 176', '2'], ['3651', '84', '343', ' 146', ' 384', ' 178', '2'], ['3652', '84', '343', ' 147', ' 383', ' 179', '2'], ['3653', '84', '342', ' 148', ' 382', ' 179', '2'], ['3654', '84', '343', ' 149', ' 383', ' 180', '2'], ['3655', '84', '342', ' 150', ' 385', ' 184', '2'], ['3656', '84', '341', ' 149', ' 386', ' 185', '2'], ['3657', '84', '341', ' 150', ' 387', ' 187', '2'], ['3658', '84', '341', ' 151', ' 388', ' 189', '2'], ['3659', '84', '342', ' 153', ' 389', ' 191', '2'], ['3660', '84', '342', ' 156', ' 388', ' 193', '2'], ['3661', '84', '342', ' 157', ' 389', ' 196', '2'], ['3662', '84', '343', ' 159', ' 390', ' 197', '2'], ['3663', '84', '344', ' 161', ' 389', ' 199', '2'], ['3664', '84', '344', ' 162', ' 390', ' 200', '2'], ['3665', '84', '344', ' 163', ' 391', ' 203', '2'], ['3666', '84', '344', ' 164', ' 392', ' 205', '2'], ['3667', '84', '344', ' 166', ' 393', ' 209', '2'], ['3668', '84', '344', ' 167', ' 394', ' 211', '2'], ['3669', '84', '344', ' 169', ' 395', ' 213', '2'], ['3670', '84', '344', ' 172', ' 394', ' 215', '2'], ['3671', '84', '344', ' 173', ' 394', ' 218', '2'], ['3672', '84', '344', ' 175', ' 396', ' 222', '2'], ['3673', '84', '344', ' 177', ' 397', ' 225', '2'], ['3674', '84', '344', ' 179', ' 398', ' 227', '2'], ['3675', '84', '344', ' 180', ' 400', ' 230', '2'], ['3676', '84', '345', ' 183', ' 401', ' 234', '2'], ['3677', '84', '345', ' 185', ' 403', ' 237', '2'], ['3678', '84', '346', ' 186', ' 405', ' 240', '2'], ['3679', '84', '346', ' 189', ' 406', ' 244', '2'], ['3680', '84', '346', ' 192', ' 406', ' 247', '2'], ['3681', '84', '344', ' 194', ' 408', ' 252', '2'], ['3682', '84', '344', ' 196', ' 410', ' 257', '2'], ['3683', '84', '344', ' 199', ' 412', ' 262', '2'], ['3684', '84', '343', ' 202', ' 412', ' 266', '2'], ['3685', '84', '344', ' 205', ' 415', ' 270', '2'], ['3686', '84', '345', ' 208', ' 417', ' 275', '2'], ['3687', '84', '346', ' 211', ' 419', ' 279', '2'], ['3688', '84', '346', ' 216', ' 420', ' 285', '2'], ['3689', '84', '346', ' 219', ' 423', ' 291', '2'], ['3690', '84', '345', ' 222', ' 425', ' 297', '2'], ['3691', '84', '344', ' 225', ' 427', ' 303', '2'], ['3692', '84', '343', ' 229', ' 429', ' 309', '2'], ['3693', '84', '345', ' 233', ' 433', ' 316', '2'], ['3694', '84', '345', ' 238', ' 436', ' 323', '2'], ['3695', '84', '347', ' 242', ' 439', ' 329', '2'], ['3696', '84', '347', ' 247', ' 442', ' 337', '2'], ['3697', '84', '346', ' 252', ' 446', ' 347', '2'], ['3698', '84', '346', ' 257', ' 448', ' 354', '2'], ['3699', '84', '347', ' 264', ' 452', ' 364', '2'], ['3700', '84', '345', ' 269', ' 455', ' 374', '2'], ['3701', '84', '344', ' 275', ' 460', ' 386', '2'], ['3702', '84', '342', ' 281', ' 465', ' 399', '2'], ['3703', '84', '342', ' 288', ' 468', ' 409', '2'], ['3704', '84', '347', ' 296', ' 470', ' 414', '2'], ['3705', '84', '351', ' 302', ' 471', ' 415', '2'], ['3706', '84', '360', ' 313', ' 472', ' 416', '2'], ['3707', '84', '368', ' 322', ' 471', ' 413', '2'], ['3708', '84', '374', ' 332', ' 470', ' 413', '2'], ['3709', '84', '380', ' 344', ' 467', ' 413', '2'], ['3710', '84', '387', ' 356', ' 463', ' 412', '2']], '79': [['3541', '79', '374', ' 107', ' 396', ' 120', '2'], ['3542', '79', '373', ' 107', ' 397', ' 121', '2'], ['3547', '79', '373', ' 108', ' 399', ' 123', '2'], ['3548', '79', '374', ' 108', ' 399', ' 124', '2'], ['3549', '79', '374', ' 108', ' 399', ' 124', '2'], ['3550', '79', '373', ' 108', ' 400', ' 124', '2'], ['3554', '79', '373', ' 108', ' 400', ' 126', '2'], ['3555', '79', '372', ' 108', ' 401', ' 127', '2'], ['3556', '79', '373', ' 109', ' 401', ' 126', '2'], ['3558', '79', '375', ' 109', ' 402', ' 127', '2'], ['3559', '79', '376', ' 110', ' 402', ' 127', '2'], ['3560', '79', '377', ' 111', ' 402', ' 127', '2'], ['3561', '79', '378', ' 112', ' 402', ' 127', '2'], ['3576', '79', '380', ' 113', ' 406', ' 129', '2'], ['3577', '79', '381', ' 113', ' 408', ' 130', '2'], ['3578', '79', '380', ' 113', ' 409', ' 131', '2'], ['3579', '79', '380', ' 113', ' 409', ' 132', '2'], ['3580', '79', '381', ' 113', ' 409', ' 132', '2'], ['3581', '79', '381', ' 113', ' 410', ' 132', '2'], ['3582', '79', '382', ' 113', ' 410', ' 132', '2'], ['3583', '79', '383', ' 113', ' 410', ' 132', '2'], ['3584', '79', '383', ' 114', ' 411', ' 133', '2'], ['3585', '79', '383', ' 114', ' 411', ' 133', '2'], ['3586', '79', '384', ' 114', ' 411', ' 133', '2'], ['3587', '79', '384', ' 114', ' 411', ' 133', '2'], ['3588', '79', '384', ' 114', ' 411', ' 133', '2'], ['3589', '79', '385', ' 115', ' 411', ' 133', '2'], ['3590', '79', '386', ' 116', ' 411', ' 134', '2'], ['3591', '79', '385', ' 116', ' 411', ' 134', '2'], ['3592', '79', '386', ' 116', ' 412', ' 135', '2'], ['3593', '79', '387', ' 117', ' 412', ' 135', '2'], ['3594', '79', '388', ' 117', ' 412', ' 135', '2'], ['3595', '79', '388', ' 118', ' 413', ' 136', '2'], ['3596', '79', '388', ' 119', ' 414', ' 137', '2'], ['3597', '79', '388', ' 119', ' 414', ' 138', '2'], ['3598', '79', '388', ' 119', ' 414', ' 138', '2'], ['3599', '79', '389', ' 120', ' 414', ' 138', '2'], ['3600', '79', '389', ' 120', ' 415', ' 139', '2'], ['3601', '79', '389', ' 120', ' 415', ' 139', '2'], ['3602', '79', '389', ' 120', ' 417', ' 139', '2'], ['3603', '79', '390', ' 120', ' 417', ' 140', '2'], ['3604', '79', '390', ' 120', ' 418', ' 140', '2'], ['3605', '79', '391', ' 120', ' 418', ' 140', '2'], ['3606', '79', '391', ' 121', ' 418', ' 140', '2'], ['3607', '79', '391', ' 121', ' 417', ' 140', '2'], ['3608', '79', '392', ' 121', ' 417', ' 140', '2'], ['3609', '79', '392', ' 121', ' 418', ' 140', '2'], ['3610', '79', '391', ' 121', ' 419', ' 141', '2'], ['3611', '79', '392', ' 121', ' 421', ' 142', '2'], ['3612', '79', '392', ' 121', ' 421', ' 142', '2'], ['3613', '79', '393', ' 122', ' 421', ' 143', '2'], ['3614', '79', '393', ' 122', ' 421', ' 143', '2'], ['3615', '79', '393', ' 122', ' 422', ' 144', '2'], ['3616', '79', '394', ' 124', ' 422', ' 145', '2'], ['3617', '79', '395', ' 125', ' 423', ' 145', '2'], ['3618', '79', '394', ' 125', ' 423', ' 145', '2'], ['3619', '79', '395', ' 125', ' 423', ' 146', '2'], ['3620', '79', '394', ' 125', ' 424', ' 146', '2'], ['3621', '79', '395', ' 125', ' 424', ' 147', '2'], ['3622', '79', '395', ' 126', ' 423', ' 147', '2'], ['3623', '79', '396', ' 127', ' 424', ' 147', '2'], ['3624', '79', '396', ' 127', ' 424', ' 147', '2'], ['3625', '79', '396', ' 127', ' 425', ' 147', '2'], ['3626', '79', '396', ' 127', ' 425', ' 148', '2'], ['3627', '79', '396', ' 128', ' 426', ' 149', '2'], ['3628', '79', '396', ' 129', ' 426', ' 150', '2'], ['3629', '79', '396', ' 129', ' 427', ' 150', '2'], ['3630', '79', '397', ' 129', ' 428', ' 151', '2'], ['3631', '79', '397', ' 129', ' 429', ' 151', '2'], ['3632', '79', '398', ' 130', ' 429', ' 152', '2'], ['3633', '79', '398', ' 131', ' 429', ' 152', '2'], ['3634', '79', '399', ' 131', ' 430', ' 152', '2'], ['3635', '79', '399', ' 131', ' 431', ' 153', '2'], ['3636', '79', '398', ' 130', ' 432', ' 153', '2'], ['3637', '79', '399', ' 130', ' 432', ' 153', '2'], ['3638', '79', '400', ' 130', ' 432', ' 153', '2'], ['3639', '79', '399', ' 131', ' 434', ' 154', '2'], ['3640', '79', '399', ' 131', ' 434', ' 155', '2'], ['3641', '79', '400', ' 131', ' 434', ' 155', '2'], ['3642', '79', '400', ' 132', ' 434', ' 155', '2'], ['3643', '79', '401', ' 133', ' 434', ' 156', '2'], ['3644', '79', '402', ' 134', ' 434', ' 156', '2'], ['3645', '79', '401', ' 133', ' 436', ' 157', '2'], ['3646', '79', '401', ' 133', ' 435', ' 157', '2'], ['3647', '79', '402', ' 134', ' 436', ' 158', '2'], ['3648', '79', '402', ' 135', ' 437', ' 159', '2'], ['3649', '79', '403', ' 136', ' 437', ' 159', '2'], ['3650', '79', '403', ' 136', ' 438', ' 160', '2'], ['3651', '79', '404', ' 136', ' 440', ' 161', '2'], ['3652', '79', '403', ' 136', ' 443', ' 163', '2'], ['3653', '79', '403', ' 136', ' 444', ' 163', '2'], ['3654', '79', '403', ' 136', ' 445', ' 164', '2'], ['3655', '79', '404', ' 138', ' 445', ' 165', '2'], ['3656', '79', '404', ' 138', ' 444', ' 166', '2'], ['3657', '79', '405', ' 139', ' 445', ' 167', '2'], ['3658', '79', '406', ' 140', ' 446', ' 167', '2'], ['3659', '79', '405', ' 140', ' 446', ' 168', '2'], ['3660', '79', '405', ' 140', ' 446', ' 168', '2'], ['3661', '79', '406', ' 140', ' 447', ' 169', '2'], ['3662', '79', '406', ' 140', ' 447', ' 170', '2'], ['3663', '79', '407', ' 140', ' 448', ' 170', '2'], ['3664', '79', '407', ' 141', ' 449', ' 171', '2'], ['3665', '79', '408', ' 142', ' 450', ' 172', '2'], ['3666', '79', '409', ' 143', ' 450', ' 173', '2'], ['3667', '79', '409', ' 144', ' 449', ' 173', '2'], ['3668', '79', '410', ' 145', ' 448', ' 173', '2'], ['3669', '79', '410', ' 146', ' 449', ' 174', '2'], ['3670', '79', '410', ' 146', ' 451', ' 175', '2'], ['3671', '79', '411', ' 146', ' 452', ' 176', '2'], ['3672', '79', '411', ' 147', ' 454', ' 177', '2'], ['3673', '79', '411', ' 147', ' 454', ' 178', '2'], ['3674', '79', '412', ' 147', ' 457', ' 180', '2'], ['3675', '79', '412', ' 147', ' 457', ' 181', '2'], ['3676', '79', '412', ' 148', ' 457', ' 182', '2'], ['3677', '79', '411', ' 149', ' 457', ' 183', '2'], ['3678', '79', '410', ' 149', ' 457', ' 184', '2'], ['3679', '79', '411', ' 150', ' 457', ' 184', '2'], ['3680', '79', '413', ' 151', ' 457', ' 184', '2'], ['3681', '79', '414', ' 152', ' 459', ' 185', '2'], ['3682', '79', '414', ' 152', ' 459', ' 186', '2'], ['3683', '79', '415', ' 153', ' 460', ' 187', '2'], ['3684', '79', '416', ' 154', ' 461', ' 188', '2'], ['3685', '79', '416', ' 155', ' 463', ' 190', '2'], ['3686', '79', '417', ' 155', ' 463', ' 191', '2'], ['3687', '79', '418', ' 157', ' 463', ' 191', '2'], ['3688', '79', '418', ' 157', ' 463', ' 192', '2'], ['3689', '79', '419', ' 158', ' 464', ' 194', '2'], ['3690', '79', '419', ' 159', ' 466', ' 195', '2'], ['3691', '79', '420', ' 160', ' 466', ' 197', '2'], ['3692', '79', '420', ' 161', ' 467', ' 198', '2'], ['3693', '79', '420', ' 161', ' 469', ' 199', '2'], ['3694', '79', '420', ' 163', ' 470', ' 202', '2'], ['3695', '79', '420', ' 163', ' 471', ' 203', '2'], ['3696', '79', '421', ' 164', ' 472', ' 204', '2'], ['3697', '79', '421', ' 164', ' 473', ' 205', '2'], ['3698', '79', '421', ' 165', ' 474', ' 206', '2'], ['3699', '79', '422', ' 166', ' 474', ' 207', '2'], ['3700', '79', '423', ' 167', ' 476', ' 209', '2'], ['3701', '79', '424', ' 167', ' 478', ' 210', '2'], ['3702', '79', '425', ' 169', ' 478', ' 211', '2'], ['3703', '79', '426', ' 170', ' 479', ' 212', '2'], ['3704', '79', '426', ' 171', ' 480', ' 214', '2'], ['3705', '79', '427', ' 173', ' 480', ' 215', '2'], ['3706', '79', '426', ' 173', ' 481', ' 217', '2'], ['3707', '79', '426', ' 173', ' 481', ' 218', '2'], ['3708', '79', '426', ' 175', ' 482', ' 220', '2'], ['3709', '79', '427', ' 176', ' 483', ' 222', '2'], ['3710', '79', '429', ' 178', ' 486', ' 224', '2'], ['3711', '79', '431', ' 179', ' 487', ' 225', '2'], ['3712', '79', '431', ' 180', ' 488', ' 227', '2'], ['3713', '79', '432', ' 180', ' 490', ' 228', '2'], ['3714', '79', '433', ' 181', ' 492', ' 230', '2'], ['3715', '79', '433', ' 183', ' 493', ' 232', '2'], ['3716', '79', '434', ' 184', ' 494', ' 234', '2'], ['3717', '79', '435', ' 186', ' 495', ' 236', '2'], ['3718', '79', '436', ' 188', ' 497', ' 238', '2'], ['3719', '79', '438', ' 191', ' 499', ' 241', '2'], ['3720', '79', '437', ' 191', ' 501', ' 244', '2'], ['3721', '79', '438', ' 192', ' 502', ' 246', '2'], ['3722', '79', '438', ' 193', ' 505', ' 248', '2'], ['3723', '79', '439', ' 195', ' 506', ' 250', '2'], ['3724', '79', '440', ' 196', ' 509', ' 253', '2'], ['3725', '79', '441', ' 198', ' 510', ' 255', '2'], ['3726', '79', '441', ' 200', ' 511', ' 258', '2'], ['3727', '79', '441', ' 201', ' 513', ' 260', '2'], ['3728', '79', '443', ' 202', ' 515', ' 262', '2'], ['3729', '79', '444', ' 204', ' 518', ' 266', '2'], ['3730', '79', '444', ' 205', ' 521', ' 270', '2'], ['3731', '79', '446', ' 207', ' 524', ' 274', '2'], ['3732', '79', '447', ' 210', ' 525', ' 276', '2'], ['3733', '79', '449', ' 213', ' 526', ' 278', '2'], ['3734', '79', '450', ' 215', ' 529', ' 282', '2'], ['3735', '79', '452', ' 218', ' 531', ' 285', '2'], ['3736', '79', '453', ' 220', ' 534', ' 289', '2'], ['3737', '79', '454', ' 221', ' 537', ' 292', '2'], ['3738', '79', '454', ' 223', ' 539', ' 296', '2'], ['3739', '79', '456', ' 225', ' 543', ' 300', '2'], ['3740', '79', '457', ' 227', ' 545', ' 303', '2'], ['3741', '79', '459', ' 230', ' 550', ' 309', '2'], ['3742', '79', '462', ' 233', ' 551', ' 311', '2'], ['3743', '79', '464', ' 236', ' 554', ' 314', '2'], ['3744', '79', '466', ' 240', ' 558', ' 320', '2'], ['3745', '79', '468', ' 242', ' 561', ' 323', '2'], ['3746', '79', '470', ' 246', ' 565', ' 329', '2'], ['3747', '79', '471', ' 249', ' 569', ' 334', '2'], ['3748', '79', '474', ' 252', ' 573', ' 338', '2'], ['3749', '79', '474', ' 255', ' 578', ' 345', '2'], ['3750', '79', '476', ' 258', ' 582', ' 350', '2'], ['3751', '79', '479', ' 262', ' 586', ' 355', '2'], ['3752', '79', '482', ' 267', ' 590', ' 361', '2'], ['3753', '79', '483', ' 270', ' 596', ' 368', '2'], ['3754', '79', '486', ' 274', ' 601', ' 374', '2'], ['3755', '79', '488', ' 279', ' 607', ' 382', '2'], ['3756', '79', '490', ' 282', ' 612', ' 388', '2'], ['3757', '79', '491', ' 286', ' 619', ' 398', '2'], ['3758', '79', '495', ' 292', ' 625', ' 406', '2'], ['3759', '79', '500', ' 296', ' 629', ' 410', '2'], ['3760', '79', '505', ' 300', ' 635', ' 414', '2'], ['3761', '79', '511', ' 306', ' 638', ' 415', '2'], ['3762', '79', '517', ' 312', ' 639', ' 415', '2'], ['3763', '79', '527', ' 317', ' 647', ' 416', '2'], ['3764', '79', '530', ' 321', ' 649', ' 417', '2'], ['3765', '79', '535', ' 327', ' 650', ' 417', '2'], ['3766', '79', '539', ' 334', ' 649', ' 415', '2']], '92': [['3666', '92', '372', ' 109', ' 394', ' 124', '2'], ['3667', '92', '372', ' 109', ' 395', ' 125', '2'], ['3668', '92', '371', ' 109', ' 395', ' 126', '2'], ['3671', '92', '372', ' 109', ' 397', ' 126', '2'], ['3672', '92', '373', ' 109', ' 396', ' 126', '2'], ['3674', '92', '374', ' 110', ' 397', ' 127', '2'], ['3675', '92', '375', ' 110', ' 398', ' 127', '2'], ['3676', '92', '375', ' 111', ' 399', ' 127', '2'], ['3677', '92', '374', ' 110', ' 400', ' 128', '2'], ['3678', '92', '375', ' 110', ' 399', ' 128', '2'], ['3679', '92', '375', ' 111', ' 399', ' 128', '2'], ['3680', '92', '375', ' 111', ' 399', ' 128', '2'], ['3681', '92', '375', ' 111', ' 400', ' 128', '2'], ['3682', '92', '376', ' 111', ' 401', ' 129', '2'], ['3685', '92', '376', ' 112', ' 402', ' 131', '2'], ['3686', '92', '376', ' 113', ' 401', ' 131', '2'], ['3687', '92', '377', ' 113', ' 402', ' 131', '2'], ['3688', '92', '377', ' 114', ' 401', ' 131', '2'], ['3689', '92', '378', ' 115', ' 402', ' 132', '2'], ['3690', '92', '378', ' 114', ' 403', ' 132', '2'], ['3691', '92', '378', ' 114', ' 404', ' 133', '2'], ['3692', '92', '378', ' 114', ' 404', ' 133', '2'], ['3693', '92', '379', ' 114', ' 405', ' 133', '2'], ['3694', '92', '380', ' 116', ' 405', ' 134', '2'], ['3695', '92', '380', ' 118', ' 404', ' 134', '2'], ['3696', '92', '381', ' 118', ' 404', ' 134', '2'], ['3697', '92', '381', ' 118', ' 405', ' 134', '2'], ['3698', '92', '381', ' 118', ' 406', ' 135', '2'], ['3699', '92', '381', ' 118', ' 406', ' 135', '2'], ['3700', '92', '381', ' 118', ' 407', ' 135', '2'], ['3701', '92', '381', ' 117', ' 408', ' 135', '2'], ['3702', '92', '381', ' 118', ' 408', ' 136', '2'], ['3703', '92', '381', ' 118', ' 409', ' 137', '2'], ['3704', '92', '381', ' 118', ' 409', ' 137', '2'], ['3705', '92', '382', ' 118', ' 409', ' 137', '2'], ['3706', '92', '382', ' 119', ' 410', ' 137', '2'], ['3707', '92', '382', ' 118', ' 410', ' 137', '2'], ['3708', '92', '382', ' 118', ' 411', ' 137', '2'], ['3709', '92', '382', ' 118', ' 411', ' 138', '2'], ['3710', '92', '383', ' 118', ' 412', ' 138', '2'], ['3711', '92', '383', ' 118', ' 412', ' 139', '2'], ['3712', '92', '384', ' 119', ' 412', ' 139', '2'], ['3713', '92', '384', ' 120', ' 412', ' 139', '2'], ['3714', '92', '385', ' 120', ' 412', ' 139', '2'], ['3715', '92', '385', ' 121', ' 411', ' 140', '2'], ['3716', '92', '385', ' 120', ' 412', ' 140', '2'], ['3717', '92', '385', ' 121', ' 412', ' 141', '2'], ['3718', '92', '385', ' 121', ' 412', ' 142', '2'], ['3719', '92', '385', ' 121', ' 413', ' 142', '2'], ['3720', '92', '386', ' 122', ' 413', ' 143', '2'], ['3721', '92', '387', ' 123', ' 413', ' 144', '2'], ['3722', '92', '387', ' 123', ' 414', ' 144', '2'], ['3723', '92', '387', ' 122', ' 415', ' 144', '2'], ['3724', '92', '387', ' 123', ' 415', ' 145', '2'], ['3725', '92', '386', ' 123', ' 415', ' 146', '2'], ['3726', '92', '387', ' 123', ' 415', ' 146', '2'], ['3727', '92', '388', ' 124', ' 416', ' 146', '2'], ['3728', '92', '389', ' 125', ' 416', ' 147', '2'], ['3729', '92', '390', ' 126', ' 416', ' 147', '2'], ['3730', '92', '390', ' 127', ' 416', ' 147', '2'], ['3731', '92', '391', ' 128', ' 418', ' 149', '2'], ['3732', '92', '390', ' 128', ' 419', ' 150', '2'], ['3733', '92', '390', ' 128', ' 419', ' 151', '2'], ['3734', '92', '390', ' 129', ' 421', ' 152', '2'], ['3735', '92', '391', ' 130', ' 422', ' 153', '2'], ['3736', '92', '391', ' 129', ' 424', ' 154', '2'], ['3737', '92', '391', ' 129', ' 423', ' 154', '2'], ['3738', '92', '391', ' 129', ' 424', ' 154', '2'], ['3739', '92', '391', ' 130', ' 424', ' 155', '2'], ['3740', '92', '391', ' 130', ' 424', ' 155', '2'], ['3741', '92', '391', ' 130', ' 424', ' 156', '2'], ['3742', '92', '392', ' 131', ' 425', ' 157', '2'], ['3743', '92', '393', ' 132', ' 425', ' 157', '2'], ['3744', '92', '393', ' 133', ' 425', ' 158', '2'], ['3745', '92', '393', ' 134', ' 424', ' 159', '2'], ['3746', '92', '393', ' 135', ' 425', ' 160', '2'], ['3747', '92', '394', ' 135', ' 426', ' 160', '2'], ['3748', '92', '395', ' 135', ' 428', ' 161', '2'], ['3749', '92', '396', ' 136', ' 429', ' 162', '2'], ['3750', '92', '396', ' 136', ' 431', ' 163', '2'], ['3751', '92', '396', ' 137', ' 433', ' 165', '2'], ['3752', '92', '395', ' 137', ' 432', ' 166', '2'], ['3753', '92', '396', ' 138', ' 434', ' 167', '2'], ['3754', '92', '396', ' 139', ' 435', ' 168', '2'], ['3755', '92', '397', ' 140', ' 435', ' 168', '2'], ['3756', '92', '398', ' 140', ' 437', ' 169', '2'], ['3757', '92', '399', ' 141', ' 439', ' 171', '2'], ['3758', '92', '399', ' 142', ' 439', ' 172', '2'], ['3759', '92', '398', ' 143', ' 439', ' 173', '2'], ['3760', '92', '399', ' 142', ' 440', ' 173', '2'], ['3761', '92', '399', ' 143', ' 439', ' 173', '2'], ['3762', '92', '400', ' 143', ' 439', ' 173', '2'], ['3763', '92', '400', ' 144', ' 439', ' 174', '2'], ['3764', '92', '401', ' 145', ' 441', ' 176', '2'], ['3765', '92', '401', ' 146', ' 440', ' 177', '2'], ['3766', '92', '400', ' 147', ' 440', ' 179', '2'], ['3767', '92', '401', ' 148', ' 441', ' 179', '2'], ['3768', '92', '402', ' 148', ' 442', ' 180', '2'], ['3769', '92', '402', ' 148', ' 444', ' 181', '2'], ['3770', '92', '404', ' 149', ' 445', ' 182', '2'], ['3771', '92', '404', ' 149', ' 445', ' 183', '2'], ['3772', '92', '404', ' 149', ' 447', ' 185', '2'], ['3773', '92', '406', ' 151', ' 447', ' 185', '2'], ['3774', '92', '407', ' 153', ' 448', ' 186', '2'], ['3775', '92', '408', ' 154', ' 449', ' 188', '2'], ['3776', '92', '409', ' 155', ' 450', ' 189', '2'], ['3777', '92', '409', ' 156', ' 451', ' 191', '2'], ['3778', '92', '411', ' 158', ' 452', ' 192', '2'], ['3779', '92', '412', ' 158', ' 454', ' 194', '2'], ['3780', '92', '413', ' 160', ' 456', ' 196', '2'], ['3781', '92', '414', ' 161', ' 457', ' 198', '2'], ['3782', '92', '414', ' 161', ' 458', ' 199', '2'], ['3783', '92', '414', ' 162', ' 459', ' 202', '2'], ['3784', '92', '415', ' 163', ' 461', ' 203', '2'], ['3785', '92', '415', ' 164', ' 463', ' 205', '2'], ['3786', '92', '417', ' 165', ' 464', ' 206', '2'], ['3787', '92', '418', ' 165', ' 467', ' 208', '2'], ['3788', '92', '420', ' 167', ' 467', ' 210', '2'], ['3789', '92', '421', ' 169', ' 469', ' 212', '2'], ['3790', '92', '422', ' 171', ' 470', ' 214', '2'], ['3791', '92', '422', ' 173', ' 470', ' 216', '2'], ['3792', '92', '423', ' 174', ' 471', ' 218', '2'], ['3793', '92', '423', ' 175', ' 474', ' 222', '2'], ['3794', '92', '424', ' 177', ' 475', ' 223', '2'], ['3795', '92', '426', ' 179', ' 477', ' 226', '2'], ['3796', '92', '427', ' 179', ' 479', ' 228', '2'], ['3797', '92', '428', ' 181', ' 481', ' 230', '2'], ['3798', '92', '430', ' 182', ' 484', ' 233', '2'], ['3799', '92', '432', ' 185', ' 486', ' 236', '2'], ['3800', '92', '433', ' 188', ' 487', ' 238', '2'], ['3801', '92', '433', ' 189', ' 490', ' 243', '2'], ['3802', '92', '434', ' 190', ' 494', ' 245', '2'], ['3803', '92', '436', ' 193', ' 494', ' 248', '2'], ['3804', '92', '436', ' 193', ' 497', ' 251', '2'], ['3805', '92', '437', ' 195', ' 500', ' 254', '2'], ['3806', '92', '438', ' 197', ' 503', ' 258', '2'], ['3807', '92', '439', ' 200', ' 504', ' 261', '2'], ['3808', '92', '442', ' 202', ' 508', ' 264', '2'], ['3809', '92', '442', ' 204', ' 510', ' 268', '2'], ['3810', '92', '444', ' 206', ' 513', ' 272', '2'], ['3811', '92', '445', ' 209', ' 515', ' 275', '2'], ['3812', '92', '447', ' 213', ' 517', ' 280', '2'], ['3813', '92', '449', ' 216', ' 519', ' 284', '2'], ['3814', '92', '450', ' 218', ' 522', ' 287', '2'], ['3815', '92', '451', ' 221', ' 527', ' 294', '2'], ['3816', '92', '453', ' 224', ' 530', ' 298', '2'], ['3817', '92', '455', ' 227', ' 533', ' 301', '2'], ['3818', '92', '457', ' 230', ' 536', ' 306', '2'], ['3819', '92', '459', ' 234', ' 540', ' 312', '2'], ['3820', '92', '461', ' 237', ' 545', ' 318', '2'], ['3821', '92', '463', ' 241', ' 549', ' 323', '2'], ['3822', '92', '466', ' 245', ' 554', ' 330', '2'], ['3823', '92', '468', ' 249', ' 560', ' 337', '2'], ['3824', '92', '470', ' 252', ' 564', ' 343', '2'], ['3825', '92', '473', ' 257', ' 567', ' 349', '2'], ['3826', '92', '476', ' 262', ' 573', ' 356', '2'], ['3827', '92', '479', ' 267', ' 577', ' 363', '2'], ['3828', '92', '481', ' 271', ' 584', ' 372', '2'], ['3829', '92', '482', ' 275', ' 591', ' 381', '2'], ['3830', '92', '486', ' 280', ' 596', ' 388', '2'], ['3831', '92', '488', ' 286', ' 603', ' 399', '2'], ['3832', '92', '493', ' 292', ' 609', ' 407', '2'], ['3833', '92', '498', ' 299', ' 613', ' 412', '2'], ['3834', '92', '504', ' 305', ' 618', ' 415', '2'], ['3835', '92', '513', ' 312', ' 623', ' 416', '2'], ['3836', '92', '521', ' 317', ' 628', ' 415', '2'], ['3837', '92', '527', ' 324', ' 627', ' 412', '2'], ['3838', '92', '533', ' 333', ' 630', ' 414', '2'], ['3839', '92', '541', ' 343', ' 631', ' 413', '2']], '101': [['4118', '101', '357', ' 105', ' 382', ' 123', '2'], ['4119', '101', '357', ' 106', ' 382', ' 124', '2'], ['4120', '101', '358', ' 107', ' 383', ' 125', '2'], ['4121', '101', '357', ' 106', ' 383', ' 125', '2'], ['4122', '101', '357', ' 106', ' 384', ' 125', '2'], ['4123', '101', '357', ' 106', ' 384', ' 125', '2'], ['4124', '101', '357', ' 106', ' 385', ' 125', '2'], ['4125', '101', '358', ' 106', ' 384', ' 126', '2'], ['4126', '101', '358', ' 106', ' 385', ' 126', '2'], ['4127', '101', '357', ' 106', ' 386', ' 126', '2'], ['4128', '101', '357', ' 106', ' 386', ' 127', '2'], ['4129', '101', '357', ' 106', ' 386', ' 127', '2'], ['4130', '101', '358', ' 106', ' 386', ' 127', '2'], ['4131', '101', '358', ' 106', ' 387', ' 127', '2'], ['4132', '101', '359', ' 106', ' 386', ' 127', '2'], ['4133', '101', '358', ' 106', ' 386', ' 127', '2'], ['4134', '101', '358', ' 105', ' 387', ' 128', '2'], ['4135', '101', '357', ' 104', ' 388', ' 129', '2'], ['4136', '101', '357', ' 103', ' 388', ' 129', '2'], ['4137', '101', '357', ' 103', ' 389', ' 129', '2'], ['4138', '101', '358', ' 103', ' 389', ' 129', '2'], ['4139', '101', '358', ' 103', ' 389', ' 130', '2'], ['4140', '101', '358', ' 102', ' 389', ' 130', '2'], ['4141', '101', '357', ' 101', ' 389', ' 130', '2'], ['4142', '101', '358', ' 101', ' 389', ' 131', '2'], ['4143', '101', '358', ' 102', ' 389', ' 131', '2'], ['4144', '101', '361', ' 106', ' 387', ' 132', '2'], ['4145', '101', '361', ' 105', ' 388', ' 132', '2'], ['4146', '101', '361', ' 105', ' 389', ' 132', '2'], ['4147', '101', '361', ' 103', ' 390', ' 133', '2'], ['4149', '101', '363', ' 107', ' 389', ' 133', '2'], ['4150', '101', '363', ' 107', ' 389', ' 134', '2'], ['4151', '101', '364', ' 110', ' 388', ' 134', '2'], ['4152', '101', '365', ' 111', ' 388', ' 134', '2'], ['4153', '101', '365', ' 112', ' 388', ' 134', '2'], ['4154', '101', '365', ' 113', ' 388', ' 135', '2'], ['4155', '101', '366', ' 114', ' 389', ' 136', '2'], ['4156', '101', '366', ' 115', ' 389', ' 137', '2'], ['4157', '101', '366', ' 116', ' 390', ' 138', '2'], ['4158', '101', '366', ' 117', ' 390', ' 138', '2'], ['4159', '101', '366', ' 119', ' 390', ' 139', '2'], ['4160', '101', '366', ' 119', ' 390', ' 140', '2'], ['4161', '101', '366', ' 118', ' 392', ' 140', '2'], ['4162', '101', '366', ' 119', ' 391', ' 141', '2'], ['4163', '101', '367', ' 120', ' 392', ' 141', '2'], ['4166', '101', '367', ' 120', ' 394', ' 142', '2'], ['4167', '101', '367', ' 120', ' 394', ' 143', '2'], ['4168', '101', '366', ' 119', ' 395', ' 143', '2'], ['4169', '101', '366', ' 120', ' 395', ' 144', '2'], ['4170', '101', '366', ' 120', ' 395', ' 144', '2'], ['4171', '101', '366', ' 121', ' 396', ' 145', '2'], ['4172', '101', '366', ' 122', ' 396', ' 146', '2'], ['4173', '101', '367', ' 122', ' 397', ' 147', '2'], ['4174', '101', '367', ' 122', ' 398', ' 147', '2'], ['4175', '101', '367', ' 122', ' 398', ' 147', '2'], ['4176', '101', '368', ' 124', ' 397', ' 148', '2'], ['4177', '101', '368', ' 124', ' 398', ' 148', '2'], ['4178', '101', '368', ' 125', ' 398', ' 149', '2'], ['4179', '101', '368', ' 126', ' 398', ' 150', '2'], ['4180', '101', '368', ' 126', ' 398', ' 151', '2'], ['4181', '101', '368', ' 127', ' 399', ' 151', '2'], ['4182', '101', '369', ' 127', ' 400', ' 152', '2'], ['4183', '101', '369', ' 127', ' 400', ' 152', '2'], ['4184', '101', '370', ' 128', ' 400', ' 153', '2'], ['4185', '101', '370', ' 129', ' 401', ' 153', '2'], ['4186', '101', '369', ' 128', ' 402', ' 154', '2'], ['4187', '101', '369', ' 128', ' 403', ' 155', '2'], ['4188', '101', '369', ' 128', ' 403', ' 155', '2'], ['4189', '101', '370', ' 128', ' 404', ' 156', '2'], ['4190', '101', '370', ' 129', ' 404', ' 157', '2'], ['4191', '101', '370', ' 129', ' 405', ' 158', '2'], ['4192', '101', '369', ' 130', ' 406', ' 160', '2'], ['4193', '101', '370', ' 130', ' 406', ' 161', '2'], ['4194', '101', '370', ' 130', ' 407', ' 161', '2'], ['4195', '101', '371', ' 131', ' 408', ' 162', '2'], ['4196', '101', '371', ' 132', ' 409', ' 164', '2'], ['4197', '101', '371', ' 132', ' 410', ' 165', '2'], ['4198', '101', '372', ' 133', ' 411', ' 166', '2'], ['4199', '101', '372', ' 134', ' 411', ' 167', '2'], ['4200', '101', '372', ' 135', ' 411', ' 168', '2'], ['4201', '101', '372', ' 135', ' 412', ' 170', '2'], ['4202', '101', '372', ' 135', ' 412', ' 170', '2'], ['4203', '101', '372', ' 136', ' 413', ' 171', '2'], ['4204', '101', '373', ' 136', ' 414', ' 172', '2'], ['4205', '101', '373', ' 136', ' 414', ' 173', '2'], ['4206', '101', '374', ' 138', ' 415', ' 174', '2'], ['4207', '101', '375', ' 140', ' 415', ' 175', '2'], ['4208', '101', '376', ' 141', ' 416', ' 177', '2'], ['4209', '101', '375', ' 141', ' 417', ' 178', '2'], ['4210', '101', '375', ' 142', ' 418', ' 179', '2'], ['4211', '101', '376', ' 144', ' 417', ' 180', '2'], ['4212', '101', '376', ' 145', ' 418', ' 182', '2'], ['4213', '101', '377', ' 147', ' 418', ' 183', '2'], ['4214', '101', '378', ' 148', ' 419', ' 184', '2'], ['4215', '101', '378', ' 148', ' 421', ' 185', '2'], ['4216', '101', '379', ' 149', ' 422', ' 186', '2'], ['4217', '101', '379', ' 151', ' 422', ' 188', '2'], ['4218', '101', '379', ' 151', ' 424', ' 190', '2'], ['4219', '101', '381', ' 152', ' 425', ' 190', '2'], ['4220', '101', '382', ' 153', ' 426', ' 191', '2'], ['4221', '101', '382', ' 154', ' 428', ' 194', '2'], ['4222', '101', '381', ' 154', ' 430', ' 197', '2'], ['4223', '101', '382', ' 155', ' 431', ' 198', '2'], ['4224', '101', '381', ' 156', ' 432', ' 201', '2'], ['4225', '101', '382', ' 156', ' 434', ' 203', '2'], ['4226', '101', '383', ' 158', ' 435', ' 205', '2'], ['4227', '101', '385', ' 161', ' 435', ' 206', '2'], ['4228', '101', '385', ' 161', ' 436', ' 207', '2'], ['4229', '101', '386', ' 162', ' 438', ' 209', '2'], ['4230', '101', '387', ' 162', ' 440', ' 211', '2'], ['4231', '101', '388', ' 164', ' 441', ' 213', '2'], ['4232', '101', '387', ' 165', ' 442', ' 216', '2'], ['4233', '101', '387', ' 166', ' 443', ' 218', '2'], ['4234', '101', '388', ' 166', ' 445', ' 221', '2'], ['4235', '101', '389', ' 168', ' 447', ' 223', '2'], ['4236', '101', '390', ' 170', ' 449', ' 226', '2'], ['4237', '101', '390', ' 171', ' 449', ' 227', '2'], ['4238', '101', '393', ' 173', ' 451', ' 229', '2'], ['4239', '101', '394', ' 175', ' 454', ' 232', '2'], ['4240', '101', '394', ' 176', ' 457', ' 236', '2'], ['4241', '101', '394', ' 177', ' 458', ' 239', '2'], ['4242', '101', '395', ' 179', ' 460', ' 242', '2'], ['4243', '101', '396', ' 182', ' 462', ' 245', '2'], ['4244', '101', '396', ' 183', ' 465', ' 249', '2'], ['4245', '101', '399', ' 186', ' 467', ' 252', '2'], ['4246', '101', '399', ' 188', ' 469', ' 255', '2'], ['4247', '101', '400', ' 190', ' 472', ' 260', '2'], ['4248', '101', '401', ' 192', ' 475', ' 264', '2'], ['4249', '101', '403', ' 195', ' 478', ' 268', '2'], ['4250', '101', '405', ' 198', ' 481', ' 271', '2'], ['4251', '101', '405', ' 201', ' 483', ' 276', '2'], ['4252', '101', '406', ' 203', ' 486', ' 281', '2'], ['4253', '101', '406', ' 206', ' 490', ' 286', '2'], ['4254', '101', '407', ' 208', ' 493', ' 291', '2'], ['4255', '101', '409', ' 211', ' 497', ' 297', '2'], ['4256', '101', '411', ' 214', ' 500', ' 300', '2'], ['4257', '101', '412', ' 217', ' 503', ' 306', '2'], ['4258', '101', '415', ' 221', ' 508', ' 312', '2'], ['4259', '101', '416', ' 224', ' 514', ' 320', '2'], ['4260', '101', '417', ' 228', ' 517', ' 326', '2'], ['4261', '101', '419', ' 232', ' 521', ' 332', '2'], ['4262', '101', '422', ' 236', ' 525', ' 337', '2'], ['4263', '101', '424', ' 241', ' 531', ' 346', '2'], ['4264', '101', '427', ' 244', ' 537', ' 353', '2'], ['4265', '101', '429', ' 249', ' 543', ' 361', '2'], ['4266', '101', '431', ' 254', ' 551', ' 373', '2'], ['4267', '101', '433', ' 259', ' 557', ' 382', '2'], ['4268', '101', '435', ' 265', ' 568', ' 396', '2'], ['4269', '101', '438', ' 270', ' 576', ' 406', '2'], ['4270', '101', '443', ' 276', ' 580', ' 411', '2'], ['4271', '101', '449', ' 282', ' 585', ' 416', '2'], ['4272', '101', '456', ' 290', ' 590', ' 420', '2'], ['4273', '101', '468', ' 297', ' 597', ' 418', '2']], '102': [['4219', '102', '364', ' 106', ' 384', ' 119', '2'], ['4220', '102', '364', ' 106', ' 384', ' 120', '2'], ['4221', '102', '365', ' 107', ' 385', ' 120', '2'], ['4222', '102', '365', ' 107', ' 385', ' 121', '2'], ['4223', '102', '365', ' 107', ' 386', ' 121', '2'], ['4224', '102', '364', ' 106', ' 386', ' 121', '2'], ['4225', '102', '364', ' 107', ' 386', ' 122', '2'], ['4226', '102', '363', ' 107', ' 386', ' 122', '2'], ['4227', '102', '364', ' 108', ' 386', ' 123', '2'], ['4228', '102', '364', ' 108', ' 386', ' 122', '2'], ['4229', '102', '363', ' 108', ' 386', ' 122', '2'], ['4230', '102', '363', ' 107', ' 386', ' 123', '2'], ['4231', '102', '362', ' 108', ' 387', ' 124', '2'], ['4232', '102', '363', ' 108', ' 387', ' 125', '2'], ['4233', '102', '363', ' 108', ' 387', ' 125', '2'], ['4234', '102', '362', ' 108', ' 387', ' 125', '2'], ['4235', '102', '362', ' 109', ' 387', ' 125', '2'], ['4236', '102', '362', ' 109', ' 387', ' 126', '2'], ['4237', '102', '362', ' 109', ' 387', ' 126', '2'], ['4238', '102', '362', ' 109', ' 388', ' 126', '2'], ['4239', '102', '363', ' 109', ' 389', ' 127', '2'], ['4240', '102', '363', ' 109', ' 389', ' 127', '2'], ['4241', '102', '364', ' 110', ' 389', ' 128', '2'], ['4242', '102', '364', ' 110', ' 389', ' 128', '2'], ['4243', '102', '364', ' 110', ' 389', ' 128', '2'], ['4244', '102', '363', ' 110', ' 389', ' 129', '2'], ['4245', '102', '364', ' 110', ' 390', ' 129', '2'], ['4246', '102', '364', ' 111', ' 390', ' 130', '2'], ['4247', '102', '365', ' 112', ' 390', ' 130', '2'], ['4248', '102', '365', ' 113', ' 389', ' 131', '2'], ['4249', '102', '364', ' 114', ' 389', ' 131', '2'], ['4250', '102', '365', ' 115', ' 389', ' 132', '2'], ['4251', '102', '366', ' 116', ' 389', ' 132', '2'], ['4252', '102', '366', ' 116', ' 390', ' 133', '2'], ['4253', '102', '367', ' 117', ' 391', ' 133', '2'], ['4254', '102', '366', ' 116', ' 392', ' 134', '2'], ['4255', '102', '366', ' 117', ' 391', ' 134', '2'], ['4256', '102', '366', ' 117', ' 392', ' 135', '2'], ['4257', '102', '367', ' 118', ' 393', ' 135', '2'], ['4258', '102', '367', ' 117', ' 394', ' 135', '2'], ['4259', '102', '366', ' 117', ' 395', ' 137', '2'], ['4260', '102', '365', ' 117', ' 395', ' 138', '2'], ['4261', '102', '364', ' 116', ' 396', ' 139', '2'], ['4262', '102', '366', ' 117', ' 396', ' 139', '2'], ['4263', '102', '366', ' 117', ' 397', ' 140', '2'], ['4264', '102', '366', ' 116', ' 399', ' 141', '2'], ['4265', '102', '366', ' 117', ' 399', ' 142', '2'], ['4266', '102', '366', ' 118', ' 398', ' 142', '2'], ['4267', '102', '367', ' 118', ' 398', ' 142', '2'], ['4268', '102', '367', ' 119', ' 398', ' 143', '2'], ['4269', '102', '368', ' 120', ' 398', ' 144', '2'], ['4270', '102', '368', ' 121', ' 397', ' 144', '2'], ['4271', '102', '369', ' 123', ' 397', ' 145', '2'], ['4272', '102', '369', ' 124', ' 398', ' 146', '2'], ['4273', '102', '370', ' 125', ' 398', ' 147', '2'], ['4274', '102', '371', ' 125', ' 399', ' 147', '2'], ['4275', '102', '371', ' 126', ' 399', ' 148', '2'], ['4276', '102', '370', ' 127', ' 400', ' 149', '2'], ['4277', '102', '369', ' 127', ' 401', ' 150', '2'], ['4278', '102', '368', ' 126', ' 401', ' 151', '2'], ['4279', '102', '369', ' 127', ' 402', ' 151', '2'], ['4280', '102', '370', ' 129', ' 401', ' 152', '2'], ['4281', '102', '369', ' 129', ' 401', ' 153', '2'], ['4282', '102', '369', ' 129', ' 402', ' 154', '2'], ['4283', '102', '368', ' 129', ' 402', ' 155', '2'], ['4284', '102', '368', ' 129', ' 403', ' 156', '2'], ['4285', '102', '368', ' 130', ' 403', ' 157', '2'], ['4286', '102', '368', ' 131', ' 404', ' 158', '2'], ['4287', '102', '369', ' 133', ' 403', ' 159', '2'], ['4288', '102', '370', ' 134', ' 403', ' 160', '2'], ['4289', '102', '369', ' 135', ' 405', ' 162', '2'], ['4290', '102', '369', ' 136', ' 406', ' 164', '2'], ['4291', '102', '370', ' 137', ' 407', ' 166', '2'], ['4292', '102', '370', ' 139', ' 406', ' 167', '2'], ['4293', '102', '371', ' 139', ' 408', ' 168', '2'], ['4294', '102', '371', ' 140', ' 408', ' 169', '2'], ['4295', '102', '370', ' 140', ' 410', ' 171', '2'], ['4296', '102', '371', ' 141', ' 410', ' 172', '2'], ['4297', '102', '372', ' 143', ' 411', ' 173', '2'], ['4298', '102', '371', ' 142', ' 412', ' 174', '2'], ['4299', '102', '371', ' 143', ' 413', ' 177', '2'], ['4300', '102', '371', ' 144', ' 414', ' 178', '2'], ['4301', '102', '372', ' 147', ' 414', ' 180', '2'], ['4302', '102', '373', ' 148', ' 415', ' 181', '2'], ['4303', '102', '373', ' 149', ' 416', ' 184', '2'], ['4304', '102', '375', ' 152', ' 417', ' 186', '2'], ['4305', '102', '376', ' 153', ' 418', ' 187', '2'], ['4306', '102', '376', ' 155', ' 419', ' 189', '2'], ['4307', '102', '378', ' 156', ' 421', ' 191', '2'], ['4308', '102', '379', ' 157', ' 423', ' 193', '2'], ['4309', '102', '380', ' 158', ' 425', ' 194', '2'], ['4310', '102', '381', ' 159', ' 427', ' 197', '2'], ['4311', '102', '381', ' 161', ' 428', ' 200', '2'], ['4312', '102', '381', ' 163', ' 430', ' 203', '2'], ['4313', '102', '382', ' 165', ' 432', ' 205', '2'], ['4314', '102', '384', ' 167', ' 433', ' 207', '2'], ['4315', '102', '386', ' 168', ' 436', ' 209', '2'], ['4316', '102', '388', ' 169', ' 440', ' 212', '2'], ['4317', '102', '387', ' 171', ' 441', ' 216', '2'], ['4318', '102', '388', ' 173', ' 444', ' 220', '2'], ['4319', '102', '389', ' 175', ' 447', ' 223', '2'], ['4320', '102', '390', ' 176', ' 449', ' 226', '2'], ['4321', '102', '392', ' 178', ' 453', ' 229', '2'], ['4322', '102', '394', ' 180', ' 456', ' 232', '2'], ['4323', '102', '396', ' 183', ' 458', ' 235', '2'], ['4324', '102', '397', ' 185', ' 463', ' 241', '2'], ['4325', '102', '400', ' 189', ' 466', ' 246', '2'], ['4326', '102', '402', ' 193', ' 468', ' 249', '2'], ['4327', '102', '405', ' 196', ' 472', ' 253', '2'], ['4328', '102', '407', ' 199', ' 477', ' 258', '2'], ['4329', '102', '409', ' 200', ' 482', ' 262', '2'], ['4330', '102', '409', ' 203', ' 487', ' 269', '2'], ['4331', '102', '412', ' 207', ' 492', ' 274', '2'], ['4332', '102', '416', ' 211', ' 496', ' 279', '2'], ['4333', '102', '417', ' 214', ' 503', ' 287', '2'], ['4334', '102', '421', ' 219', ' 509', ' 294', '2'], ['4335', '102', '424', ' 222', ' 515', ' 300', '2'], ['4336', '102', '426', ' 226', ' 521', ' 307', '2'], ['4337', '102', '432', ' 231', ' 528', ' 314', '2'], ['4338', '102', '435', ' 236', ' 536', ' 322', '2'], ['4339', '102', '439', ' 242', ' 543', ' 330', '2'], ['4340', '102', '444', ' 248', ' 551', ' 340', '2'], ['4341', '102', '450', ' 254', ' 560', ' 349', '2'], ['4342', '102', '455', ' 261', ' 571', ' 360', '2'], ['4343', '102', '461', ' 267', ' 581', ' 371', '2'], ['4344', '102', '466', ' 274', ' 592', ' 383', '2'], ['4345', '102', '471', ' 281', ' 605', ' 398', '2'], ['4346', '102', '479', ' 290', ' 616', ' 409', '2'], ['4347', '102', '491', ' 298', ' 626', ' 415', '2'], ['4348', '102', '504', ' 307', ' 640', ' 421', '2'], ['4349', '102', '518', ' 317', ' 643', ' 419', '2'], ['4350', '102', '532', ' 328', ' 646', ' 417', '2']], '109': [['4420', '109', '350', ' 111', ' 373', ' 130', '2'], ['4424', '109', '348', ' 108', ' 377', ' 131', '2'], ['4425', '109', '349', ' 109', ' 377', ' 132', '2'], ['4426', '109', '350', ' 111', ' 377', ' 133', '2'], ['4427', '109', '351', ' 112', ' 377', ' 134', '2'], ['4428', '109', '351', ' 112', ' 377', ' 134', '2'], ['4429', '109', '351', ' 113', ' 377', ' 134', '2'], ['4430', '109', '351', ' 113', ' 377', ' 134', '2'], ['4431', '109', '351', ' 113', ' 377', ' 134', '2'], ['4432', '109', '353', ' 114', ' 377', ' 135', '2'], ['4433', '109', '352', ' 114', ' 378', ' 136', '2'], ['4434', '109', '352', ' 114', ' 379', ' 137', '2'], ['4435', '109', '352', ' 113', ' 380', ' 137', '2'], ['4436', '109', '352', ' 113', ' 381', ' 138', '2'], ['4437', '109', '352', ' 113', ' 381', ' 138', '2'], ['4438', '109', '351', ' 112', ' 382', ' 138', '2'], ['4439', '109', '352', ' 112', ' 382', ' 139', '2'], ['4440', '109', '352', ' 113', ' 382', ' 139', '2'], ['4441', '109', '353', ' 114', ' 382', ' 140', '2'], ['4442', '109', '354', ' 114', ' 383', ' 140', '2'], ['4443', '109', '355', ' 115', ' 383', ' 140', '2'], ['4444', '109', '354', ' 115', ' 384', ' 140', '2'], ['4445', '109', '354', ' 115', ' 384', ' 141', '2'], ['4446', '109', '355', ' 115', ' 384', ' 141', '2'], ['4447', '109', '356', ' 116', ' 383', ' 141', '2'], ['4448', '109', '356', ' 116', ' 384', ' 141', '2'], ['4449', '109', '356', ' 117', ' 384', ' 141', '2'], ['4450', '109', '356', ' 117', ' 385', ' 142', '2'], ['4451', '109', '356', ' 117', ' 385', ' 143', '2'], ['4452', '109', '357', ' 117', ' 385', ' 143', '2'], ['4453', '109', '357', ' 118', ' 385', ' 143', '2'], ['4454', '109', '357', ' 118', ' 386', ' 144', '2'], ['4455', '109', '358', ' 119', ' 385', ' 144', '2'], ['4456', '109', '358', ' 119', ' 386', ' 144', '2'], ['4457', '109', '357', ' 119', ' 386', ' 145', '2'], ['4458', '109', '358', ' 120', ' 386', ' 145', '2'], ['4459', '109', '359', ' 121', ' 386', ' 146', '2'], ['4460', '109', '359', ' 122', ' 387', ' 146', '2'], ['4461', '109', '359', ' 122', ' 387', ' 147', '2'], ['4462', '109', '359', ' 122', ' 387', ' 147', '2'], ['4463', '109', '360', ' 122', ' 388', ' 147', '2'], ['4464', '109', '361', ' 123', ' 388', ' 147', '2'], ['4465', '109', '361', ' 124', ' 389', ' 147', '2'], ['4466', '109', '361', ' 124', ' 390', ' 149', '2'], ['4467', '109', '361', ' 125', ' 391', ' 150', '2'], ['4468', '109', '361', ' 125', ' 391', ' 151', '2'], ['4469', '109', '360', ' 126', ' 392', ' 151', '2'], ['4470', '109', '361', ' 126', ' 392', ' 152', '2'], ['4471', '109', '362', ' 127', ' 393', ' 152', '2'], ['4472', '109', '362', ' 127', ' 394', ' 152', '2'], ['4473', '109', '363', ' 127', ' 394', ' 153', '2'], ['4474', '109', '363', ' 128', ' 395', ' 153', '2'], ['4475', '109', '363', ' 128', ' 395', ' 154', '2'], ['4476', '109', '364', ' 128', ' 396', ' 154', '2'], ['4477', '109', '364', ' 128', ' 396', ' 155', '2'], ['4478', '109', '364', ' 129', ' 397', ' 156', '2'], ['4479', '109', '364', ' 129', ' 397', ' 156', '2'], ['4480', '109', '365', ' 129', ' 399', ' 157', '2'], ['4481', '109', '365', ' 129', ' 400', ' 158', '2'], ['4482', '109', '365', ' 129', ' 400', ' 158', '2'], ['4483', '109', '364', ' 129', ' 400', ' 158', '2'], ['4484', '109', '365', ' 129', ' 401', ' 159', '2'], ['4485', '109', '365', ' 130', ' 402', ' 160', '2'], ['4486', '109', '364', ' 130', ' 402', ' 161', '2'], ['4487', '109', '365', ' 130', ' 403', ' 163', '2'], ['4488', '109', '366', ' 131', ' 404', ' 164', '2'], ['4489', '109', '367', ' 132', ' 405', ' 164', '2'], ['4490', '109', '367', ' 131', ' 406', ' 165', '2'], ['4491', '109', '367', ' 131', ' 406', ' 165', '2'], ['4492', '109', '368', ' 132', ' 406', ' 166', '2'], ['4493', '109', '369', ' 133', ' 407', ' 167', '2'], ['4494', '109', '369', ' 134', ' 408', ' 168', '2'], ['4495', '109', '369', ' 135', ' 408', ' 169', '2'], ['4496', '109', '370', ' 135', ' 409', ' 170', '2'], ['4497', '109', '370', ' 136', ' 410', ' 171', '2'], ['4498', '109', '370', ' 136', ' 410', ' 171', '2'], ['4499', '109', '371', ' 136', ' 411', ' 171', '2'], ['4500', '109', '371', ' 138', ' 411', ' 173', '2'], ['4501', '109', '371', ' 139', ' 411', ' 174', '2'], ['4502', '109', '372', ' 140', ' 412', ' 175', '2'], ['4503', '109', '373', ' 140', ' 414', ' 176', '2'], ['4504', '109', '374', ' 140', ' 415', ' 177', '2'], ['4505', '109', '374', ' 141', ' 416', ' 178', '2'], ['4506', '109', '374', ' 142', ' 416', ' 179', '2'], ['4507', '109', '375', ' 142', ' 416', ' 180', '2'], ['4508', '109', '375', ' 144', ' 417', ' 181', '2'], ['4509', '109', '376', ' 145', ' 418', ' 182', '2'], ['4510', '109', '376', ' 145', ' 419', ' 183', '2'], ['4511', '109', '377', ' 147', ' 419', ' 185', '2'], ['4512', '109', '378', ' 147', ' 421', ' 186', '2'], ['4513', '109', '378', ' 147', ' 422', ' 187', '2'], ['4514', '109', '379', ' 148', ' 423', ' 188', '2'], ['4515', '109', '379', ' 149', ' 423', ' 189', '2'], ['4516', '109', '380', ' 150', ' 424', ' 189', '2'], ['4517', '109', '381', ' 150', ' 425', ' 190', '2'], ['4518', '109', '381', ' 151', ' 427', ' 193', '2'], ['4519', '109', '381', ' 151', ' 429', ' 194', '2'], ['4520', '109', '381', ' 151', ' 431', ' 197', '2'], ['4521', '109', '382', ' 154', ' 431', ' 199', '2'], ['4522', '109', '383', ' 154', ' 433', ' 201', '2'], ['4523', '109', '385', ' 156', ' 434', ' 202', '2'], ['4524', '109', '385', ' 157', ' 435', ' 204', '2'], ['4525', '109', '385', ' 157', ' 436', ' 205', '2'], ['4526', '109', '386', ' 158', ' 437', ' 207', '2'], ['4527', '109', '388', ' 160', ' 439', ' 208', '2'], ['4528', '109', '390', ' 162', ' 441', ' 209', '2'], ['4529', '109', '390', ' 162', ' 442', ' 211', '2'], ['4530', '109', '390', ' 163', ' 444', ' 213', '2'], ['4531', '109', '389', ' 162', ' 446', ' 215', '2'], ['4532', '109', '389', ' 163', ' 447', ' 216', '2'], ['4533', '109', '390', ' 165', ' 448', ' 219', '2'], ['4534', '109', '391', ' 168', ' 450', ' 223', '2'], ['4535', '109', '392', ' 169', ' 452', ' 225', '2'], ['4536', '109', '393', ' 171', ' 454', ' 227', '2'], ['4537', '109', '394', ' 173', ' 454', ' 228', '2'], ['4538', '109', '396', ' 174', ' 456', ' 230', '2'], ['4539', '109', '396', ' 175', ' 458', ' 233', '2'], ['4540', '109', '398', ' 176', ' 459', ' 233', '2'], ['4541', '109', '400', ' 179', ' 462', ' 236', '2'], ['4542', '109', '401', ' 182', ' 465', ' 240', '2'], ['4543', '109', '401', ' 183', ' 467', ' 243', '2'], ['4544', '109', '401', ' 184', ' 471', ' 248', '2'], ['4545', '109', '403', ' 186', ' 474', ' 251', '2'], ['4546', '109', '405', ' 188', ' 477', ' 254', '2'], ['4547', '109', '408', ' 192', ' 477', ' 255', '2'], ['4548', '109', '408', ' 193', ' 481', ' 260', '2'], ['4549', '109', '410', ' 195', ' 484', ' 262', '2'], ['4550', '109', '411', ' 196', ' 488', ' 265', '2'], ['4551', '109', '414', ' 200', ' 491', ' 269', '2'], ['4552', '109', '415', ' 201', ' 495', ' 274', '2'], ['4553', '109', '416', ' 203', ' 499', ' 278', '2'], ['4554', '109', '417', ' 205', ' 503', ' 282', '2'], ['4555', '109', '418', ' 208', ' 505', ' 286', '2'], ['4556', '109', '419', ' 209', ' 510', ' 292', '2'], ['4557', '109', '421', ' 212', ' 513', ' 296', '2'], ['4558', '109', '423', ' 214', ' 517', ' 299', '2'], ['4559', '109', '426', ' 217', ' 521', ' 303', '2'], ['4560', '109', '427', ' 219', ' 527', ' 310', '2'], ['4561', '109', '430', ' 223', ' 532', ' 316', '2'], ['4562', '109', '432', ' 226', ' 536', ' 322', '2'], ['4563', '109', '435', ' 230', ' 541', ' 328', '2'], ['4564', '109', '436', ' 232', ' 547', ' 334', '2'], ['4565', '109', '440', ' 236', ' 551', ' 339', '2'], ['4566', '109', '442', ' 241', ' 557', ' 347', '2'], ['4567', '109', '446', ' 244', ' 564', ' 354', '2'], ['4569', '109', '452', ' 252', ' 575', ' 366', '2'], ['4570', '109', '455', ' 258', ' 583', ' 376', '2'], ['4571', '109', '460', ' 263', ' 591', ' 384', '2'], ['4572', '109', '461', ' 268', ' 602', ' 400', '2'], ['4573', '109', '466', ' 274', ' 610', ' 408', '2'], ['4574', '109', '473', ' 278', ' 617', ' 413', '2'], ['4575', '109', '481', ' 284', ' 621', ' 414', '2'], ['4576', '109', '489', ' 291', ' 626', ' 415', '2'], ['4577', '109', '500', ' 298', ' 634', ' 416', '2'], ['4578', '109', '507', ' 303', ' 636', ' 414', '2'], ['4579', '109', '514', ' 310', ' 637', ' 412', '2'], ['4580', '109', '523', ' 318', ' 643', ' 413', '2'], ['4581', '109', '532', ' 325', ' 648', ' 413', '2'], ['4582', '109', '542', ' 332', ' 653', ' 412', '2'], ['4583', '109', '556', ' 342', ' 656', ' 410', '2'], ['4584', '109', '563', ' 350', ' 658', ' 411', '2'], ['4585', '109', '574', ' 360', ' 661', ' 412', '2']], '117': [['4811', '117', '342', ' 117', ' 367', ' 134', '2'], ['4812', '117', '341', ' 118', ' 368', ' 135', '2'], ['4813', '117', '340', ' 118', ' 368', ' 136', '2'], ['4815', '117', '341', ' 122', ' 366', ' 138', '2'], ['4821', '117', '341', ' 127', ' 367', ' 143', '2'], ['4822', '117', '341', ' 127', ' 368', ' 144', '2'], ['4823', '117', '341', ' 128', ' 367', ' 145', '2'], ['4825', '117', '340', ' 129', ' 367', ' 147', '2'], ['4826', '117', '339', ' 129', ' 368', ' 147', '2'], ['4827', '117', '338', ' 129', ' 369', ' 149', '2'], ['4828', '117', '338', ' 129', ' 370', ' 150', '2'], ['4829', '117', '338', ' 129', ' 371', ' 151', '2'], ['4830', '117', '338', ' 130', ' 371', ' 152', '2'], ['4831', '117', '339', ' 132', ' 372', ' 153', '2'], ['4832', '117', '340', ' 134', ' 370', ' 154', '2'], ['4833', '117', '340', ' 135', ' 371', ' 155', '2'], ['4834', '117', '338', ' 135', ' 372', ' 156', '2'], ['4835', '117', '338', ' 135', ' 373', ' 157', '2'], ['4836', '117', '336', ' 135', ' 373', ' 158', '2'], ['4837', '117', '336', ' 137', ' 372', ' 159', '2'], ['4838', '117', '337', ' 137', ' 373', ' 160', '2'], ['4839', '117', '338', ' 141', ' 372', ' 162', '2'], ['4840', '117', '336', ' 140', ' 374', ' 164', '2'], ['4841', '117', '336', ' 140', ' 374', ' 165', '2'], ['4842', '117', '336', ' 141', ' 375', ' 166', '2'], ['4843', '117', '335', ' 140', ' 377', ' 168', '2'], ['4844', '117', '334', ' 141', ' 377', ' 169', '2'], ['4845', '117', '334', ' 142', ' 377', ' 171', '2'], ['4846', '117', '333', ' 143', ' 378', ' 173', '2'], ['4847', '117', '333', ' 144', ' 376', ' 174', '2'], ['4848', '117', '333', ' 144', ' 379', ' 177', '2'], ['4849', '117', '333', ' 145', ' 380', ' 178', '2'], ['4850', '117', '332', ' 146', ' 379', ' 180', '2'], ['4851', '117', '332', ' 147', ' 380', ' 182', '2'], ['4852', '117', '332', ' 149', ' 379', ' 184', '2'], ['4853', '117', '331', ' 149', ' 379', ' 185', '2'], ['4854', '117', '332', ' 150', ' 380', ' 186', '2'], ['4855', '117', '331', ' 152', ' 380', ' 189', '2'], ['4856', '117', '333', ' 154', ' 380', ' 191', '2'], ['4857', '117', '333', ' 155', ' 381', ' 193', '2'], ['4858', '117', '332', ' 157', ' 381', ' 196', '2'], ['4859', '117', '332', ' 159', ' 381', ' 199', '2'], ['4860', '117', '332', ' 161', ' 382', ' 201', '2'], ['4861', '117', '332', ' 163', ' 383', ' 204', '2'], ['4862', '117', '333', ' 166', ' 382', ' 206', '2'], ['4863', '117', '333', ' 168', ' 383', ' 209', '2'], ['4864', '117', '334', ' 169', ' 384', ' 211', '2'], ['4865', '117', '333', ' 171', ' 385', ' 214', '2'], ['4866', '117', '332', ' 173', ' 385', ' 218', '2'], ['4867', '117', '331', ' 175', ' 387', ' 222', '2'], ['4868', '117', '331', ' 176', ' 388', ' 225', '2'], ['4869', '117', '330', ' 177', ' 390', ' 228', '2'], ['4870', '117', '331', ' 181', ' 391', ' 232', '2'], ['4871', '117', '333', ' 184', ' 393', ' 236', '2'], ['4872', '117', '334', ' 189', ' 393', ' 240', '2'], ['4873', '117', '331', ' 190', ' 395', ' 246', '2'], ['4874', '117', '330', ' 193', ' 395', ' 249', '2'], ['4875', '117', '331', ' 196', ' 398', ' 255', '2'], ['4876', '117', '330', ' 199', ' 401', ' 261', '2'], ['4877', '117', '330', ' 203', ' 401', ' 266', '2'], ['4878', '117', '330', ' 208', ' 404', ' 274', '2'], ['4879', '117', '329', ' 211', ' 405', ' 279', '2'], ['4880', '117', '330', ' 215', ' 408', ' 284', '2'], ['4881', '117', '328', ' 219', ' 410', ' 291', '2'], ['4882', '117', '329', ' 223', ' 413', ' 298', '2'], ['4883', '117', '329', ' 227', ' 416', ' 306', '2'], ['4884', '117', '330', ' 234', ' 420', ' 315', '2'], ['4885', '117', '331', ' 240', ' 423', ' 323', '2'], ['4886', '117', '332', ' 245', ' 427', ' 332', '2'], ['4887', '117', '332', ' 252', ' 431', ' 343', '2'], ['4888', '117', '332', ' 258', ' 435', ' 353', '2'], ['4889', '117', '333', ' 266', ' 440', ' 365', '2'], ['4890', '117', '330', ' 273', ' 445', ' 379', '2'], ['4891', '117', '328', ' 280', ' 451', ' 394', '2'], ['4892', '117', '327', ' 288', ' 455', ' 406', '2'], ['4893', '117', '331', ' 299', ' 457', ' 414', '2'], ['4894', '117', '339', ' 309', ' 459', ' 417', '2'], ['4895', '117', '348', ' 320', ' 451', ' 409', '2'], ['4896', '117', '355', ' 332', ' 452', ' 412', '2'], ['4897', '117', '363', ' 346', ' 450', ' 413', '2'], ['4898', '117', '370', ' 362', ' 443', ' 413', '2']], '122': [['4848', '122', '357', ' 117', ' 383', ' 137', '2'], ['4849', '122', '357', ' 118', ' 383', ' 138', '2'], ['4850', '122', '356', ' 117', ' 384', ' 139', '2'], ['4853', '122', '356', ' 117', ' 384', ' 139', '2'], ['4858', '122', '356', ' 125', ' 382', ' 145', '2'], ['4861', '122', '357', ' 127', ' 383', ' 147', '2'], ['4862', '122', '357', ' 128', ' 383', ' 147', '2'], ['4863', '122', '357', ' 128', ' 384', ' 148', '2'], ['4864', '122', '356', ' 128', ' 386', ' 150', '2'], ['4865', '122', '355', ' 128', ' 387', ' 151', '2'], ['4866', '122', '355', ' 129', ' 388', ' 152', '2'], ['4867', '122', '355', ' 129', ' 388', ' 153', '2'], ['4868', '122', '356', ' 130', ' 387', ' 153', '2'], ['4869', '122', '356', ' 131', ' 387', ' 154', '2'], ['4870', '122', '355', ' 130', ' 388', ' 155', '2'], ['4871', '122', '355', ' 131', ' 388', ' 156', '2'], ['4872', '122', '354', ' 132', ' 388', ' 157', '2'], ['4873', '122', '354', ' 132', ' 389', ' 158', '2'], ['4874', '122', '355', ' 133', ' 389', ' 159', '2'], ['4875', '122', '355', ' 134', ' 388', ' 160', '2'], ['4876', '122', '355', ' 135', ' 389', ' 162', '2'], ['4877', '122', '355', ' 135', ' 391', ' 162', '2'], ['4878', '122', '355', ' 136', ' 392', ' 164', '2'], ['4879', '122', '354', ' 136', ' 393', ' 166', '2'], ['4880', '122', '355', ' 138', ' 394', ' 167', '2'], ['4881', '122', '353', ' 138', ' 393', ' 168', '2'], ['4882', '122', '354', ' 139', ' 392', ' 169', '2'], ['4883', '122', '355', ' 141', ' 395', ' 171', '2'], ['4884', '122', '354', ' 141', ' 394', ' 172', '2'], ['4885', '122', '353', ' 142', ' 394', ' 173', '2'], ['4886', '122', '354', ' 144', ' 394', ' 174', '2'], ['4887', '122', '354', ' 145', ' 393', ' 175', '2'], ['4888', '122', '354', ' 147', ' 395', ' 178', '2'], ['4889', '122', '354', ' 148', ' 395', ' 179', '2'], ['4890', '122', '354', ' 149', ' 395', ' 180', '2'], ['4891', '122', '353', ' 150', ' 395', ' 182', '2'], ['4892', '122', '353', ' 151', ' 396', ' 184', '2'], ['4893', '122', '353', ' 152', ' 397', ' 185', '2'], ['4894', '122', '353', ' 153', ' 397', ' 186', '2'], ['4895', '122', '353', ' 153', ' 398', ' 188', '2'], ['4896', '122', '353', ' 155', ' 399', ' 190', '2'], ['4897', '122', '354', ' 156', ' 399', ' 191', '2'], ['4898', '122', '353', ' 158', ' 400', ' 194', '2'], ['4899', '122', '353', ' 159', ' 401', ' 196', '2'], ['4900', '122', '354', ' 160', ' 402', ' 199', '2'], ['4901', '122', '354', ' 161', ' 403', ' 200', '2'], ['4902', '122', '353', ' 162', ' 403', ' 202', '2'], ['4903', '122', '353', ' 162', ' 403', ' 204', '2'], ['4904', '122', '353', ' 165', ' 403', ' 207', '2'], ['4905', '122', '353', ' 166', ' 404', ' 209', '2'], ['4906', '122', '354', ' 168', ' 406', ' 211', '2'], ['4907', '122', '353', ' 170', ' 406', ' 214', '2'], ['4908', '122', '354', ' 173', ' 406', ' 217', '2'], ['4909', '122', '353', ' 174', ' 407', ' 220', '2'], ['4910', '122', '354', ' 176', ' 407', ' 223', '2'], ['4911', '122', '355', ' 178', ' 410', ' 226', '2'], ['4912', '122', '354', ' 179', ' 410', ' 228', '2'], ['4913', '122', '354', ' 181', ' 412', ' 232', '2'], ['4914', '122', '353', ' 182', ' 413', ' 236', '2'], ['4915', '122', '353', ' 185', ' 414', ' 239', '2'], ['4916', '122', '354', ' 188', ' 416', ' 243', '2'], ['4917', '122', '355', ' 191', ' 419', ' 247', '2'], ['4918', '122', '355', ' 194', ' 419', ' 252', '2'], ['4919', '122', '354', ' 195', ' 421', ' 256', '2'], ['4920', '122', '354', ' 199', ' 423', ' 260', '2'], ['4921', '122', '354', ' 202', ' 424', ' 265', '2'], ['4922', '122', '353', ' 204', ' 426', ' 271', '2'], ['4923', '122', '355', ' 208', ' 428', ' 274', '2'], ['4924', '122', '356', ' 212', ' 430', ' 279', '2'], ['4925', '122', '357', ' 216', ' 433', ' 284', '2'], ['4926', '122', '356', ' 219', ' 436', ' 292', '2'], ['4927', '122', '356', ' 222', ' 439', ' 298', '2'], ['4928', '122', '356', ' 227', ' 441', ' 305', '2'], ['4929', '122', '357', ' 231', ' 444', ' 311', '2'], ['4930', '122', '357', ' 237', ' 446', ' 318', '2'], ['4931', '122', '358', ' 241', ' 449', ' 325', '2'], ['4932', '122', '358', ' 247', ' 452', ' 334', '2'], ['4933', '122', '357', ' 252', ' 455', ' 343', '2'], ['4934', '122', '358', ' 258', ' 460', ' 351', '2'], ['4935', '122', '359', ' 265', ' 464', ' 361', '2'], ['4936', '122', '358', ' 271', ' 468', ' 372', '2'], ['4937', '122', '357', ' 278', ' 474', ' 386', '2'], ['4938', '122', '356', ' 286', ' 480', ' 400', '2'], ['4939', '122', '359', ' 293', ' 485', ' 409', '2'], ['4940', '122', '363', ' 301', ' 488', ' 415', '2'], ['4941', '122', '368', ' 310', ' 489', ' 419', '2'], ['4942', '122', '379', ' 319', ' 481', ' 407', '2']], '136': [['5412', '136', '379', ' 105', ' 396', ' 118', '2'], ['5415', '136', '380', ' 105', ' 396', ' 119', '2'], ['5420', '136', '380', ' 106', ' 397', ' 119', '2'], ['5422', '136', '380', ' 106', ' 397', ' 120', '2'], ['5423', '136', '380', ' 106', ' 398', ' 121', '2'], ['5425', '136', '381', ' 107', ' 398', ' 121', '2'], ['5427', '136', '382', ' 107', ' 398', ' 121', '2'], ['5429', '136', '382', ' 108', ' 399', ' 121', '2'], ['5430', '136', '382', ' 108', ' 399', ' 122', '2'], ['5431', '136', '382', ' 108', ' 399', ' 122', '2'], ['5441', '136', '383', ' 108', ' 404', ' 124', '2'], ['5443', '136', '385', ' 109', ' 406', ' 126', '2'], ['5444', '136', '386', ' 110', ' 407', ' 127', '2'], ['5445', '136', '386', ' 111', ' 407', ' 127', '2'], ['5446', '136', '386', ' 111', ' 406', ' 127', '2'], ['5447', '136', '386', ' 111', ' 406', ' 127', '2'], ['5448', '136', '386', ' 111', ' 407', ' 127', '2'], ['5449', '136', '386', ' 112', ' 407', ' 128', '2'], ['5450', '136', '386', ' 112', ' 408', ' 129', '2'], ['5451', '136', '386', ' 112', ' 408', ' 129', '2'], ['5452', '136', '386', ' 112', ' 409', ' 130', '2'], ['5453', '136', '386', ' 111', ' 409', ' 130', '2'], ['5454', '136', '386', ' 112', ' 409', ' 130', '2'], ['5455', '136', '386', ' 112', ' 409', ' 131', '2'], ['5456', '136', '386', ' 112', ' 410', ' 131', '2'], ['5457', '136', '387', ' 112', ' 410', ' 132', '2'], ['5458', '136', '387', ' 113', ' 410', ' 132', '2'], ['5459', '136', '387', ' 113', ' 410', ' 132', '2'], ['5460', '136', '388', ' 114', ' 411', ' 133', '2'], ['5461', '136', '388', ' 114', ' 411', ' 134', '2'], ['5462', '136', '388', ' 115', ' 411', ' 134', '2'], ['5463', '136', '389', ' 116', ' 411', ' 135', '2'], ['5464', '136', '389', ' 116', ' 412', ' 135', '2'], ['5465', '136', '389', ' 116', ' 412', ' 135', '2'], ['5466', '136', '390', ' 116', ' 412', ' 135', '2'], ['5467', '136', '391', ' 117', ' 412', ' 134', '2'], ['5468', '136', '391', ' 117', ' 412', ' 134', '2'], ['5469', '136', '390', ' 117', ' 413', ' 136', '2'], ['5470', '136', '391', ' 117', ' 414', ' 137', '2'], ['5471', '136', '392', ' 118', ' 415', ' 138', '2'], ['5472', '136', '392', ' 118', ' 416', ' 138', '2'], ['5473', '136', '393', ' 118', ' 417', ' 139', '2'], ['5474', '136', '393', ' 118', ' 419', ' 139', '2'], ['5475', '136', '394', ' 118', ' 420', ' 140', '2'], ['5476', '136', '394', ' 118', ' 420', ' 140', '2'], ['5477', '136', '394', ' 117', ' 421', ' 141', '2'], ['5478', '136', '394', ' 117', ' 421', ' 141', '2'], ['5479', '136', '396', ' 119', ' 421', ' 142', '2'], ['5480', '136', '396', ' 120', ' 422', ' 142', '2'], ['5481', '136', '397', ' 120', ' 422', ' 143', '2'], ['5482', '136', '396', ' 121', ' 422', ' 143', '2'], ['5483', '136', '396', ' 121', ' 422', ' 144', '2'], ['5484', '136', '396', ' 122', ' 422', ' 145', '2'], ['5485', '136', '397', ' 123', ' 423', ' 145', '2'], ['5486', '136', '398', ' 124', ' 423', ' 146', '2'], ['5487', '136', '398', ' 125', ' 423', ' 147', '2'], ['5488', '136', '399', ' 125', ' 424', ' 147', '2'], ['5489', '136', '400', ' 125', ' 425', ' 147', '2'], ['5490', '136', '400', ' 126', ' 426', ' 147', '2'], ['5491', '136', '401', ' 126', ' 427', ' 148', '2'], ['5492', '136', '401', ' 127', ' 429', ' 150', '2'], ['5493', '136', '400', ' 126', ' 430', ' 151', '2'], ['5494', '136', '400', ' 127', ' 431', ' 152', '2'], ['5495', '136', '400', ' 126', ' 433', ' 152', '2'], ['5496', '136', '401', ' 126', ' 434', ' 153', '2'], ['5497', '136', '402', ' 126', ' 435', ' 154', '2'], ['5498', '136', '402', ' 127', ' 435', ' 154', '2'], ['5499', '136', '403', ' 127', ' 436', ' 155', '2'], ['5500', '136', '404', ' 128', ' 437', ' 155', '2'], ['5501', '136', '405', ' 129', ' 438', ' 156', '2'], ['5502', '136', '406', ' 130', ' 438', ' 157', '2'], ['5503', '136', '405', ' 130', ' 440', ' 158', '2'], ['5504', '136', '406', ' 129', ' 440', ' 158', '2'], ['5505', '136', '406', ' 129', ' 441', ' 159', '2'], ['5506', '136', '408', ' 130', ' 442', ' 159', '2'], ['5507', '136', '408', ' 131', ' 443', ' 161', '2'], ['5508', '136', '410', ' 133', ' 444', ' 162', '2'], ['5509', '136', '411', ' 133', ' 446', ' 163', '2'], ['5510', '136', '412', ' 134', ' 447', ' 164', '2'], ['5511', '136', '413', ' 135', ' 448', ' 164', '2'], ['5512', '136', '414', ' 135', ' 449', ' 165', '2'], ['5513', '136', '414', ' 136', ' 450', ' 166', '2'], ['5514', '136', '415', ' 137', ' 451', ' 167', '2'], ['5515', '136', '415', ' 137', ' 452', ' 168', '2'], ['5516', '136', '416', ' 138', ' 452', ' 169', '2'], ['5517', '136', '416', ' 139', ' 454', ' 171', '2'], ['5518', '136', '418', ' 140', ' 455', ' 172', '2'], ['5519', '136', '418', ' 141', ' 456', ' 174', '2'], ['5520', '136', '419', ' 141', ' 457', ' 175', '2'], ['5521', '136', '420', ' 142', ' 458', ' 176', '2'], ['5522', '136', '422', ' 143', ' 461', ' 178', '2'], ['5523', '136', '422', ' 144', ' 461', ' 179', '2'], ['5524', '136', '423', ' 145', ' 463', ' 180', '2'], ['5525', '136', '424', ' 145', ' 463', ' 181', '2'], ['5526', '136', '425', ' 147', ' 464', ' 181', '2'], ['5527', '136', '427', ' 148', ' 465', ' 183', '2'], ['5528', '136', '428', ' 147', ' 468', ' 184', '2'], ['5529', '136', '429', ' 149', ' 469', ' 185', '2'], ['5530', '136', '431', ' 150', ' 471', ' 186', '2'], ['5531', '136', '432', ' 152', ' 472', ' 188', '2'], ['5532', '136', '434', ' 152', ' 475', ' 189', '2'], ['5533', '136', '434', ' 153', ' 476', ' 191', '2'], ['5534', '136', '435', ' 154', ' 477', ' 193', '2'], ['5535', '136', '436', ' 155', ' 479', ' 194', '2'], ['5536', '136', '437', ' 156', ' 481', ' 196', '2'], ['5537', '136', '439', ' 157', ' 483', ' 198', '2'], ['5538', '136', '441', ' 158', ' 485', ' 199', '2'], ['5539', '136', '441', ' 159', ' 487', ' 202', '2'], ['5540', '136', '442', ' 160', ' 489', ' 204', '2'], ['5541', '136', '443', ' 161', ' 490', ' 205', '2'], ['5542', '136', '445', ' 163', ' 493', ' 206', '2'], ['5543', '136', '446', ' 163', ' 495', ' 208', '2'], ['5544', '136', '448', ' 166', ' 497', ' 210', '2'], ['5545', '136', '449', ' 167', ' 499', ' 212', '2'], ['5546', '136', '450', ' 168', ' 501', ' 214', '2'], ['5548', '136', '451', ' 169', ' 505', ' 219', '2'], ['5549', '136', '453', ' 170', ' 508', ' 221', '2'], ['5550', '136', '456', ' 174', ' 510', ' 224', '2'], ['5551', '136', '458', ' 176', ' 513', ' 226', '2'], ['5552', '136', '458', ' 176', ' 516', ' 229', '2'], ['5553', '136', '461', ' 177', ' 518', ' 231', '2'], ['5554', '136', '463', ' 179', ' 520', ' 233', '2'], ['5555', '136', '464', ' 180', ' 524', ' 235', '2'], ['5556', '136', '466', ' 181', ' 527', ' 239', '2'], ['5557', '136', '468', ' 183', ' 531', ' 243', '2'], ['5558', '136', '470', ' 185', ' 534', ' 245', '2'], ['5559', '136', '473', ' 188', ' 537', ' 248', '2'], ['5560', '136', '477', ' 193', ' 539', ' 251', '2'], ['5561', '136', '477', ' 192', ' 543', ' 255', '2'], ['5562', '136', '480', ' 194', ' 547', ' 257', '2'], ['5563', '136', '482', ' 196', ' 551', ' 260', '2'], ['5564', '136', '484', ' 197', ' 555', ' 262', '2'], ['5565', '136', '486', ' 199', ' 559', ' 267', '2'], ['5566', '136', '488', ' 201', ' 563', ' 272', '2'], ['5567', '136', '491', ' 202', ' 568', ' 274', '2'], ['5568', '136', '494', ' 205', ' 571', ' 278', '2'], ['5569', '136', '497', ' 208', ' 575', ' 282', '2'], ['5570', '136', '501', ' 212', ' 579', ' 285', '2'], ['5571', '136', '504', ' 215', ' 584', ' 290', '2'], ['5572', '136', '508', ' 218', ' 589', ' 296', '2'], ['5573', '136', '512', ' 221', ' 596', ' 300', '2'], ['5574', '136', '516', ' 223', ' 604', ' 306', '2'], ['5575', '136', '520', ' 226', ' 610', ' 311', '2'], ['5576', '136', '522', ' 229', ' 614', ' 316', '2'], ['5577', '136', '526', ' 232', ' 621', ' 323', '2'], ['5578', '136', '531', ' 236', ' 628', ' 329', '2'], ['5579', '136', '535', ' 241', ' 634', ' 335', '2'], ['5580', '136', '540', ' 245', ' 641', ' 341', '2'], ['5581', '136', '545', ' 248', ' 649', ' 347', '2'], ['5582', '136', '549', ' 252', ' 657', ' 354', '2'], ['5583', '136', '554', ' 256', ' 665', ' 362', '2'], ['5584', '136', '560', ' 261', ' 674', ' 369', '2'], ['5585', '136', '565', ' 266', ' 683', ' 378', '2'], ['5586', '136', '571', ' 270', ' 693', ' 386', '2'], ['5587', '136', '577', ' 275', ' 704', ' 397', '2'], ['5588', '136', '582', ' 280', ' 714', ' 406', '2'], ['5589', '136', '591', ' 285', ' 724', ' 412', '2'], ['5590', '136', '601', ' 292', ' 732', ' 416', '2'], ['5591', '136', '615', ' 298', ' 743', ' 416', '2'], ['5592', '136', '624', ' 305', ' 750', ' 417', '2'], ['5593', '136', '634', ' 312', ' 753', ' 415', '2'], ['5594', '136', '643', ' 320', ' 757', ' 415', '2'], ['5595', '136', '650', ' 327', ' 759', ' 414', '2'], ['5596', '136', '660', ' 335', ' 760', ' 413', '2'], ['5597', '136', '669', ' 344', ' 759', ' 411', '2']], '140': [['5555', '140', '377', ' 108', ' 400', ' 121', '2'], ['5556', '140', '378', ' 108', ' 401', ' 122', '2'], ['5557', '140', '380', ' 109', ' 403', ' 122', '2'], ['5558', '140', '380', ' 110', ' 405', ' 124', '2'], ['5560', '140', '379', ' 109', ' 407', ' 126', '2'], ['5561', '140', '378', ' 107', ' 408', ' 126', '2'], ['5574', '140', '389', ' 113', ' 417', ' 131', '2'], ['5575', '140', '389', ' 114', ' 417', ' 132', '2'], ['5576', '140', '390', ' 115', ' 417', ' 132', '2'], ['5577', '140', '391', ' 115', ' 418', ' 132', '2'], ['5578', '140', '392', ' 115', ' 419', ' 132', '2'], ['5579', '140', '393', ' 116', ' 419', ' 133', '2'], ['5580', '140', '395', ' 116', ' 421', ' 133', '2'], ['5581', '140', '394', ' 115', ' 422', ' 133', '2'], ['5582', '140', '395', ' 116', ' 422', ' 134', '2'], ['5583', '140', '397', ' 116', ' 422', ' 134', '2'], ['5584', '140', '398', ' 117', ' 423', ' 135', '2'], ['5585', '140', '398', ' 118', ' 424', ' 135', '2'], ['5586', '140', '398', ' 118', ' 424', ' 136', '2'], ['5587', '140', '399', ' 119', ' 425', ' 138', '2'], ['5588', '140', '399', ' 120', ' 426', ' 138', '2'], ['5589', '140', '401', ' 120', ' 428', ' 140', '2'], ['5590', '140', '402', ' 119', ' 429', ' 139', '2'], ['5591', '140', '402', ' 119', ' 430', ' 140', '2'], ['5592', '140', '404', ' 120', ' 431', ' 140', '2'], ['5593', '140', '403', ' 119', ' 432', ' 141', '2'], ['5594', '140', '405', ' 121', ' 432', ' 141', '2'], ['5595', '140', '406', ' 122', ' 433', ' 142', '2'], ['5596', '140', '407', ' 123', ' 434', ' 143', '2'], ['5597', '140', '408', ' 124', ' 433', ' 143', '2'], ['5598', '140', '408', ' 124', ' 435', ' 143', '2'], ['5599', '140', '408', ' 123', ' 437', ' 145', '2'], ['5600', '140', '408', ' 123', ' 438', ' 145', '2'], ['5601', '140', '410', ' 124', ' 439', ' 145', '2'], ['5602', '140', '411', ' 125', ' 440', ' 146', '2'], ['5603', '140', '413', ' 127', ' 440', ' 146', '2'], ['5604', '140', '414', ' 129', ' 441', ' 147', '2'], ['5605', '140', '414', ' 128', ' 445', ' 149', '2'], ['5606', '140', '414', ' 128', ' 447', ' 150', '2'], ['5607', '140', '415', ' 128', ' 448', ' 151', '2'], ['5608', '140', '416', ' 129', ' 449', ' 152', '2'], ['5609', '140', '417', ' 130', ' 449', ' 152', '2'], ['5610', '140', '417', ' 130', ' 450', ' 153', '2'], ['5611', '140', '417', ' 131', ' 451', ' 154', '2'], ['5612', '140', '417', ' 131', ' 452', ' 156', '2'], ['5613', '140', '417', ' 132', ' 453', ' 157', '2'], ['5614', '140', '419', ' 132', ' 454', ' 157', '2'], ['5615', '140', '419', ' 132', ' 455', ' 158', '2'], ['5616', '140', '420', ' 134', ' 456', ' 159', '2'], ['5617', '140', '420', ' 134', ' 457', ' 161', '2'], ['5618', '140', '421', ' 135', ' 459', ' 162', '2'], ['5619', '140', '421', ' 135', ' 460', ' 163', '2'], ['5620', '140', '422', ' 135', ' 462', ' 164', '2'], ['5621', '140', '423', ' 136', ' 463', ' 165', '2'], ['5622', '140', '425', ' 138', ' 463', ' 166', '2'], ['5623', '140', '426', ' 139', ' 465', ' 167', '2'], ['5624', '140', '426', ' 139', ' 466', ' 168', '2'], ['5625', '140', '427', ' 140', ' 468', ' 171', '2'], ['5626', '140', '426', ' 141', ' 469', ' 172', '2'], ['5627', '140', '427', ' 141', ' 471', ' 173', '2'], ['5628', '140', '428', ' 142', ' 471', ' 174', '2'], ['5629', '140', '431', ' 144', ' 474', ' 176', '2'], ['5630', '140', '433', ' 145', ' 475', ' 177', '2'], ['5631', '140', '433', ' 146', ' 475', ' 179', '2'], ['5632', '140', '433', ' 147', ' 477', ' 181', '2'], ['5633', '140', '434', ' 148', ' 479', ' 182', '2'], ['5634', '140', '436', ' 150', ' 479', ' 183', '2'], ['5635', '140', '435', ' 149', ' 481', ' 185', '2'], ['5636', '140', '438', ' 153', ' 480', ' 186', '2'], ['5637', '140', '440', ' 156', ' 482', ' 189', '2'], ['5638', '140', '442', ' 157', ' 484', ' 190', '2'], ['5639', '140', '441', ' 157', ' 486', ' 192', '2'], ['5640', '140', '442', ' 158', ' 488', ' 194', '2'], ['5641', '140', '443', ' 160', ' 489', ' 196', '2'], ['5642', '140', '444', ' 161', ' 491', ' 197', '2'], ['5643', '140', '444', ' 161', ' 494', ' 200', '2'], ['5644', '140', '446', ' 163', ' 497', ' 203', '2'], ['5645', '140', '446', ' 165', ' 498', ' 205', '2'], ['5646', '140', '448', ' 167', ' 500', ' 208', '2'], ['5647', '140', '449', ' 168', ' 502', ' 210', '2'], ['5648', '140', '451', ' 170', ' 505', ' 212', '2'], ['5649', '140', '452', ' 172', ' 506', ' 215', '2'], ['5650', '140', '453', ' 174', ' 508', ' 217', '2'], ['5651', '140', '454', ' 176', ' 510', ' 220', '2'], ['5652', '140', '455', ' 178', ' 513', ' 224', '2'], ['5653', '140', '456', ' 180', ' 516', ' 227', '2'], ['5654', '140', '457', ' 180', ' 519', ' 229', '2'], ['5655', '140', '458', ' 182', ' 522', ' 232', '2'], ['5656', '140', '460', ' 185', ' 525', ' 237', '2'], ['5657', '140', '461', ' 188', ' 527', ' 239', '2'], ['5658', '140', '465', ' 191', ' 530', ' 243', '2'], ['5659', '140', '466', ' 194', ' 533', ' 246', '2'], ['5660', '140', '468', ' 196', ' 537', ' 250', '2'], ['5661', '140', '469', ' 198', ' 541', ' 255', '2'], ['5662', '140', '471', ' 201', ' 543', ' 258', '2'], ['5663', '140', '473', ' 203', ' 547', ' 262', '2'], ['5664', '140', '474', ' 206', ' 553', ' 268', '2'], ['5665', '140', '477', ' 210', ' 556', ' 272', '2'], ['5666', '140', '479', ' 212', ' 561', ' 278', '2'], ['5667', '140', '482', ' 217', ' 567', ' 284', '2'], ['5668', '140', '485', ' 220', ' 571', ' 288', '2'], ['5669', '140', '487', ' 223', ' 577', ' 295', '2'], ['5670', '140', '491', ' 228', ' 582', ' 300', '2'], ['5671', '140', '493', ' 230', ' 588', ' 307', '2'], ['5672', '140', '496', ' 234', ' 594', ' 313', '2'], ['5673', '140', '500', ' 240', ' 600', ' 320', '2'], ['5674', '140', '503', ' 244', ' 607', ' 328', '2'], ['5675', '140', '507', ' 249', ' 614', ' 336', '2'], ['5676', '140', '511', ' 254', ' 622', ' 344', '2'], ['5677', '140', '516', ' 259', ' 631', ' 352', '2'], ['5678', '140', '521', ' 266', ' 639', ' 362', '2'], ['5679', '140', '526', ' 272', ' 650', ' 373', '2'], ['5680', '140', '530', ' 277', ' 660', ' 384', '2'], ['5681', '140', '534', ' 284', ' 671', ' 397', '2'], ['5682', '140', '541', ' 292', ' 681', ' 408', '2'], ['5683', '140', '551', ' 301', ' 689', ' 414', '2'], ['5684', '140', '565', ' 309', ' 700', ' 416', '2'], ['5685', '140', '579', ' 317', ' 710', ' 418', '2'], ['5686', '140', '589', ' 326', ' 708', ' 414', '2'], ['5687', '140', '602', ' 339', ' 709', ' 414', '2'], ['5688', '140', '614', ' 349', ' 712', ' 413', '2'], ['5689', '140', '628', ' 362', ' 712', ' 412', '2']], '139': [['5505', '139', '343', ' 106', ' 367', ' 121', '2'], ['5506', '139', '343', ' 106', ' 367', ' 121', '2'], ['5507', '139', '344', ' 106', ' 368', ' 121', '2'], ['5508', '139', '343', ' 106', ' 368', ' 122', '2'], ['5509', '139', '344', ' 107', ' 369', ' 122', '2'], ['5510', '139', '343', ' 107', ' 370', ' 123', '2'], ['5511', '139', '344', ' 107', ' 370', ' 124', '2'], ['5512', '139', '343', ' 107', ' 370', ' 124', '2'], ['5513', '139', '344', ' 107', ' 370', ' 124', '2'], ['5521', '139', '345', ' 107', ' 372', ' 125', '2'], ['5522', '139', '345', ' 108', ' 372', ' 125', '2'], ['5523', '139', '346', ' 108', ' 371', ' 126', '2'], ['5524', '139', '346', ' 108', ' 371', ' 126', '2'], ['5525', '139', '346', ' 109', ' 371', ' 126', '2'], ['5526', '139', '347', ' 108', ' 372', ' 126', '2'], ['5527', '139', '347', ' 109', ' 372', ' 126', '2'], ['5528', '139', '348', ' 109', ' 372', ' 126', '2'], ['5529', '139', '348', ' 109', ' 373', ' 126', '2'], ['5530', '139', '348', ' 109', ' 373', ' 126', '2'], ['5531', '139', '348', ' 108', ' 373', ' 126', '2'], ['5532', '139', '348', ' 109', ' 373', ' 127', '2'], ['5533', '139', '349', ' 109', ' 373', ' 127', '2'], ['5534', '139', '348', ' 109', ' 373', ' 127', '2'], ['5535', '139', '348', ' 109', ' 373', ' 127', '2'], ['5536', '139', '348', ' 109', ' 373', ' 127', '2'], ['5537', '139', '348', ' 109', ' 373', ' 127', '2'], ['5538', '139', '348', ' 108', ' 374', ' 127', '2'], ['5539', '139', '349', ' 109', ' 375', ' 128', '2'], ['5540', '139', '349', ' 109', ' 375', ' 128', '2'], ['5541', '139', '349', ' 109', ' 375', ' 128', '2'], ['5542', '139', '349', ' 109', ' 375', ' 128', '2'], ['5543', '139', '350', ' 110', ' 375', ' 128', '2'], ['5544', '139', '350', ' 110', ' 375', ' 129', '2'], ['5545', '139', '349', ' 110', ' 375', ' 129', '2'], ['5546', '139', '349', ' 110', ' 375', ' 130', '2'], ['5547', '139', '349', ' 110', ' 376', ' 130', '2'], ['5548', '139', '349', ' 110', ' 376', ' 130', '2'], ['5550', '139', '351', ' 112', ' 375', ' 131', '2'], ['5551', '139', '350', ' 112', ' 375', ' 131', '2'], ['5552', '139', '351', ' 112', ' 376', ' 132', '2'], ['5553', '139', '351', ' 112', ' 376', ' 132', '2'], ['5554', '139', '351', ' 112', ' 377', ' 132', '2'], ['5555', '139', '351', ' 113', ' 377', ' 133', '2'], ['5556', '139', '352', ' 113', ' 378', ' 133', '2'], ['5557', '139', '352', ' 113', ' 379', ' 134', '2'], ['5558', '139', '352', ' 113', ' 379', ' 134', '2'], ['5559', '139', '353', ' 113', ' 379', ' 134', '2'], ['5560', '139', '353', ' 113', ' 380', ' 134', '2'], ['5561', '139', '353', ' 113', ' 380', ' 134', '2'], ['5562', '139', '353', ' 113', ' 381', ' 135', '2'], ['5563', '139', '354', ' 113', ' 381', ' 135', '2'], ['5564', '139', '353', ' 112', ' 382', ' 135', '2'], ['5565', '139', '353', ' 113', ' 383', ' 136', '2'], ['5566', '139', '353', ' 113', ' 384', ' 137', '2'], ['5567', '139', '353', ' 112', ' 384', ' 137', '2'], ['5570', '139', '354', ' 114', ' 384', ' 139', '2'], ['5571', '139', '354', ' 114', ' 384', ' 139', '2'], ['5572', '139', '354', ' 114', ' 385', ' 139', '2'], ['5573', '139', '355', ' 114', ' 386', ' 140', '2'], ['5574', '139', '354', ' 115', ' 386', ' 140', '2'], ['5575', '139', '355', ' 115', ' 386', ' 141', '2'], ['5576', '139', '353', ' 115', ' 386', ' 141', '2'], ['5577', '139', '354', ' 115', ' 386', ' 141', '2'], ['5578', '139', '354', ' 115', ' 385', ' 141', '2'], ['5579', '139', '354', ' 115', ' 386', ' 142', '2'], ['5580', '139', '354', ' 115', ' 385', ' 142', '2'], ['5581', '139', '354', ' 115', ' 386', ' 142', '2'], ['5582', '139', '354', ' 115', ' 386', ' 143', '2'], ['5583', '139', '355', ' 116', ' 386', ' 143', '2'], ['5584', '139', '355', ' 117', ' 385', ' 144', '2'], ['5585', '139', '356', ' 118', ' 384', ' 144', '2'], ['5586', '139', '357', ' 119', ' 384', ' 144', '2'], ['5587', '139', '357', ' 120', ' 384', ' 145', '2'], ['5588', '139', '358', ' 121', ' 385', ' 146', '2'], ['5589', '139', '358', ' 122', ' 385', ' 146', '2'], ['5590', '139', '358', ' 123', ' 385', ' 147', '2'], ['5591', '139', '358', ' 124', ' 384', ' 147', '2'], ['5592', '139', '358', ' 125', ' 384', ' 148', '2'], ['5593', '139', '359', ' 126', ' 384', ' 148', '2'], ['5594', '139', '359', ' 126', ' 385', ' 148', '2'], ['5595', '139', '359', ' 126', ' 385', ' 149', '2'], ['5596', '139', '358', ' 127', ' 386', ' 150', '2'], ['5597', '139', '358', ' 127', ' 387', ' 150', '2'], ['5598', '139', '357', ' 126', ' 387', ' 151', '2'], ['5599', '139', '358', ' 127', ' 387', ' 151', '2'], ['5600', '139', '357', ' 127', ' 387', ' 151', '2'], ['5601', '139', '357', ' 127', ' 388', ' 152', '2'], ['5602', '139', '357', ' 127', ' 388', ' 152', '2'], ['5603', '139', '357', ' 127', ' 388', ' 152', '2'], ['5604', '139', '358', ' 128', ' 388', ' 153', '2'], ['5605', '139', '357', ' 128', ' 389', ' 154', '2'], ['5606', '139', '358', ' 129', ' 389', ' 154', '2'], ['5607', '139', '358', ' 129', ' 390', ' 155', '2'], ['5608', '139', '358', ' 130', ' 390', ' 155', '2'], ['5609', '139', '357', ' 130', ' 391', ' 157', '2'], ['5610', '139', '357', ' 130', ' 391', ' 157', '2'], ['5611', '139', '358', ' 132', ' 392', ' 159', '2'], ['5612', '139', '359', ' 133', ' 392', ' 159', '2'], ['5613', '139', '359', ' 133', ' 393', ' 160', '2'], ['5614', '139', '359', ' 134', ' 393', ' 161', '2'], ['5615', '139', '359', ' 134', ' 394', ' 162', '2'], ['5616', '139', '360', ' 135', ' 394', ' 163', '2'], ['5617', '139', '360', ' 136', ' 396', ' 164', '2'], ['5618', '139', '359', ' 136', ' 397', ' 165', '2'], ['5619', '139', '359', ' 136', ' 397', ' 166', '2'], ['5620', '139', '358', ' 136', ' 397', ' 166', '2'], ['5621', '139', '359', ' 136', ' 398', ' 167', '2'], ['5622', '139', '359', ' 137', ' 398', ' 168', '2'], ['5623', '139', '359', ' 137', ' 398', ' 169', '2'], ['5624', '139', '359', ' 138', ' 398', ' 170', '2'], ['5625', '139', '359', ' 138', ' 399', ' 171', '2'], ['5626', '139', '359', ' 138', ' 400', ' 172', '2'], ['5627', '139', '359', ' 139', ' 400', ' 173', '2'], ['5628', '139', '359', ' 139', ' 401', ' 173', '2'], ['5629', '139', '360', ' 139', ' 401', ' 174', '2'], ['5630', '139', '359', ' 140', ' 402', ' 176', '2'], ['5631', '139', '360', ' 140', ' 402', ' 177', '2'], ['5632', '139', '361', ' 143', ' 401', ' 178', '2'], ['5633', '139', '360', ' 144', ' 401', ' 179', '2'], ['5634', '139', '360', ' 144', ' 402', ' 180', '2'], ['5635', '139', '360', ' 145', ' 402', ' 182', '2'], ['5636', '139', '360', ' 146', ' 402', ' 182', '2'], ['5637', '139', '361', ' 147', ' 403', ' 183', '2'], ['5638', '139', '361', ' 148', ' 404', ' 184', '2'], ['5639', '139', '361', ' 148', ' 404', ' 186', '2'], ['5640', '139', '360', ' 148', ' 405', ' 187', '2'], ['5641', '139', '360', ' 149', ' 406', ' 189', '2'], ['5642', '139', '361', ' 151', ' 406', ' 190', '2'], ['5643', '139', '362', ' 152', ' 407', ' 191', '2'], ['5644', '139', '363', ' 153', ' 409', ' 193', '2'], ['5645', '139', '364', ' 154', ' 409', ' 194', '2'], ['5646', '139', '364', ' 156', ' 409', ' 195', '2'], ['5647', '139', '363', ' 157', ' 410', ' 197', '2'], ['5648', '139', '363', ' 158', ' 410', ' 199', '2'], ['5649', '139', '363', ' 159', ' 411', ' 200', '2'], ['5650', '139', '364', ' 160', ' 412', ' 202', '2'], ['5651', '139', '365', ' 161', ' 413', ' 203', '2'], ['5652', '139', '365', ' 163', ' 414', ' 205', '2'], ['5653', '139', '365', ' 164', ' 415', ' 207', '2'], ['5654', '139', '365', ' 164', ' 417', ' 209', '2'], ['5655', '139', '365', ' 165', ' 418', ' 211', '2'], ['5656', '139', '365', ' 166', ' 418', ' 212', '2'], ['5657', '139', '366', ' 167', ' 419', ' 213', '2'], ['5658', '139', '367', ' 168', ' 420', ' 215', '2'], ['5659', '139', '368', ' 170', ' 421', ' 217', '2'], ['5660', '139', '368', ' 172', ' 423', ' 220', '2'], ['5661', '139', '368', ' 173', ' 424', ' 224', '2'], ['5662', '139', '368', ' 175', ' 425', ' 226', '2'], ['5663', '139', '370', ' 176', ' 427', ' 227', '2'], ['5664', '139', '371', ' 177', ' 428', ' 228', '2'], ['5665', '139', '371', ' 178', ' 430', ' 230', '2'], ['5666', '139', '371', ' 180', ' 431', ' 233', '2'], ['5667', '139', '371', ' 182', ' 432', ' 237', '2'], ['5668', '139', '371', ' 183', ' 434', ' 239', '2'], ['5669', '139', '373', ' 186', ' 435', ' 242', '2'], ['5670', '139', '373', ' 187', ' 438', ' 245', '2'], ['5671', '139', '373', ' 189', ' 441', ' 250', '2'], ['5672', '139', '375', ' 192', ' 443', ' 253', '2'], ['5673', '139', '376', ' 194', ' 443', ' 255', '2'], ['5674', '139', '377', ' 196', ' 445', ' 257', '2'], ['5675', '139', '379', ' 199', ' 448', ' 261', '2'], ['5676', '139', '380', ' 200', ' 451', ' 264', '2'], ['5677', '139', '381', ' 202', ' 453', ' 268', '2'], ['5678', '139', '382', ' 204', ' 455', ' 271', '2'], ['5679', '139', '383', ' 206', ' 458', ' 274', '2'], ['5680', '139', '383', ' 208', ' 459', ' 278', '2'], ['5681', '139', '384', ' 210', ' 463', ' 282', '2'], ['5682', '139', '386', ' 213', ' 467', ' 287', '2'], ['5683', '139', '388', ' 215', ' 468', ' 289', '2'], ['5684', '139', '390', ' 218', ' 471', ' 293', '2'], ['5685', '139', '390', ' 219', ' 474', ' 298', '2'], ['5688', '139', '393', ' 225', ' 485', ' 313', '2'], ['5689', '139', '394', ' 227', ' 490', ' 319', '2'], ['5690', '139', '395', ' 229', ' 495', ' 325', '2'], ['5691', '139', '397', ' 233', ' 497', ' 329', '2'], ['5692', '139', '399', ' 239', ' 502', ' 337', '2'], ['5693', '139', '402', ' 243', ' 506', ' 342', '2'], ['5694', '139', '404', ' 247', ' 511', ' 348', '2'], ['5695', '139', '407', ' 252', ' 517', ' 356', '2'], ['5696', '139', '408', ' 255', ' 522', ' 363', '2'], ['5697', '139', '410', ' 260', ' 528', ' 371', '2'], ['5698', '139', '413', ' 265', ' 535', ' 380', '2'], ['5699', '139', '414', ' 268', ' 542', ' 389', '2'], ['5700', '139', '414', ' 274', ' 550', ' 403', '2'], ['5701', '139', '418', ' 279', ' 557', ' 409', '2'], ['5702', '139', '425', ' 284', ' 563', ' 412', '2'], ['5703', '139', '433', ' 290', ' 566', ' 413', '2'], ['5704', '139', '440', ' 297', ' 572', ' 416', '2'], ['5705', '139', '446', ' 303', ' 575', ' 415', '2'], ['5706', '139', '453', ' 310', ' 579', ' 416', '2'], ['5707', '139', '461', ' 318', ' 581', ' 416', '2'], ['5708', '139', '470', ' 324', ' 584', ' 414', '2'], ['5709', '139', '477', ' 330', ' 590', ' 414', '2'], ['5710', '139', '484', ' 342', ' 587', ' 413', '2'], ['5711', '139', '494', ' 351', ' 587', ' 411', '2']], '153': [['6473', '153', '351', ' 118', ' 377', ' 135', '2'], ['6474', '153', '350', ' 116', ' 378', ' 135', '2'], ['6475', '153', '350', ' 116', ' 378', ' 135', '2'], ['6477', '153', '352', ' 118', ' 378', ' 135', '2'], ['6478', '153', '350', ' 118', ' 379', ' 137', '2'], ['6481', '153', '350', ' 118', ' 380', ' 138', '2'], ['6482', '153', '349', ' 118', ' 382', ' 139', '2'], ['6483', '153', '348', ' 118', ' 383', ' 141', '2'], ['6484', '153', '347', ' 117', ' 384', ' 142', '2'], ['6494', '153', '351', ' 123', ' 384', ' 145', '2'], ['6496', '153', '356', ' 129', ' 384', ' 147', '2'], ['6497', '153', '355', ' 131', ' 385', ' 150', '2'], ['6498', '153', '353', ' 128', ' 387', ' 151', '2'], ['6499', '153', '352', ' 127', ' 389', ' 151', '2'], ['6500', '153', '351', ' 128', ' 389', ' 152', '2'], ['6501', '153', '352', ' 128', ' 389', ' 153', '2'], ['6504', '153', '352', ' 130', ' 389', ' 154', '2'], ['6506', '153', '353', ' 131', ' 390', ' 156', '2'], ['6508', '153', '352', ' 132', ' 392', ' 159', '2'], ['6509', '153', '354', ' 135', ' 393', ' 162', '2'], ['6510', '153', '355', ' 136', ' 395', ' 163', '2'], ['6511', '153', '355', ' 137', ' 397', ' 165', '2'], ['6512', '153', '354', ' 137', ' 398', ' 167', '2'], ['6513', '153', '354', ' 137', ' 399', ' 168', '2'], ['6514', '153', '353', ' 136', ' 400', ' 169', '2'], ['6515', '153', '353', ' 137', ' 399', ' 170', '2'], ['6516', '153', '352', ' 137', ' 400', ' 171', '2'], ['6517', '153', '352', ' 138', ' 399', ' 172', '2'], ['6518', '153', '353', ' 139', ' 400', ' 173', '2'], ['6519', '153', '354', ' 140', ' 400', ' 175', '2'], ['6520', '153', '354', ' 141', ' 400', ' 176', '2'], ['6521', '153', '353', ' 142', ' 401', ' 179', '2'], ['6522', '153', '354', ' 144', ' 401', ' 180', '2'], ['6523', '153', '354', ' 145', ' 401', ' 182', '2'], ['6524', '153', '355', ' 147', ' 401', ' 184', '2'], ['6525', '153', '355', ' 149', ' 401', ' 186', '2'], ['6526', '153', '356', ' 150', ' 402', ' 187', '2'], ['6527', '153', '357', ' 151', ' 403', ' 188', '2'], ['6528', '153', '357', ' 152', ' 404', ' 190', '2'], ['6529', '153', '358', ' 153', ' 406', ' 192', '2'], ['6530', '153', '359', ' 156', ' 406', ' 194', '2'], ['6531', '153', '357', ' 155', ' 408', ' 198', '2'], ['6532', '153', '357', ' 155', ' 410', ' 200', '2'], ['6533', '153', '358', ' 155', ' 413', ' 201', '2'], ['6534', '153', '360', ' 158', ' 414', ' 204', '2'], ['6535', '153', '360', ' 159', ' 415', ' 206', '2'], ['6536', '153', '361', ' 162', ' 415', ' 208', '2'], ['6537', '153', '362', ' 164', ' 416', ' 210', '2'], ['6538', '153', '362', ' 165', ' 418', ' 214', '2'], ['6539', '153', '362', ' 167', ' 420', ' 217', '2'], ['6540', '153', '361', ' 167', ' 422', ' 220', '2'], ['6541', '153', '362', ' 170', ' 423', ' 223', '2'], ['6542', '153', '363', ' 173', ' 424', ' 226', '2'], ['6543', '153', '363', ' 174', ' 425', ' 229', '2'], ['6544', '153', '364', ' 176', ' 427', ' 232', '2'], ['6545', '153', '366', ' 177', ' 430', ' 234', '2'], ['6546', '153', '366', ' 179', ' 432', ' 238', '2'], ['6547', '153', '367', ' 183', ' 433', ' 242', '2'], ['6548', '153', '367', ' 184', ' 436', ' 246', '2'], ['6549', '153', '367', ' 188', ' 438', ' 251', '2'], ['6550', '153', '370', ' 193', ' 440', ' 256', '2'], ['6551', '153', '369', ' 192', ' 444', ' 260', '2'], ['6552', '153', '370', ' 194', ' 447', ' 264', '2'], ['6553', '153', '371', ' 198', ' 450', ' 269', '2'], ['6554', '153', '372', ' 201', ' 454', ' 275', '2'], ['6555', '153', '373', ' 203', ' 457', ' 279', '2'], ['6556', '153', '375', ' 208', ' 460', ' 285', '2'], ['6557', '153', '375', ' 210', ' 463', ' 290', '2'], ['6558', '153', '377', ' 214', ' 467', ' 298', '2'], ['6559', '153', '379', ' 220', ' 472', ' 305', '2'], ['6560', '153', '380', ' 224', ' 476', ' 312', '2'], ['6561', '153', '381', ' 228', ' 481', ' 319', '2'], ['6562', '153', '383', ' 233', ' 485', ' 328', '2'], ['6563', '153', '385', ' 238', ' 491', ' 336', '2'], ['6564', '153', '387', ' 244', ' 497', ' 345', '2'], ['6565', '153', '389', ' 248', ' 504', ' 355', '2'], ['6566', '153', '391', ' 254', ' 511', ' 365', '2'], ['6567', '153', '393', ' 261', ' 519', ' 377', '2'], ['6568', '153', '396', ' 268', ' 526', ' 389', '2'], ['6569', '153', '397', ' 275', ' 535', ' 404', '2'], ['6570', '153', '402', ' 282', ' 541', ' 411', '2'], ['6571', '153', '410', ' 290', ' 545', ' 415', '2'], ['6572', '153', '421', ' 300', ' 552', ' 418', '2'], ['6573', '153', '430', ' 309', ' 554', ' 416', '2'], ['6575', '153', '446', ' 326', ' 556', ' 416', '2'], ['6576', '153', '457', ' 342', ' 552', ' 414', '2']], '154': [['6626', '154', '370', ' 107', ' 393', ' 122', '2'], ['6627', '154', '372', ' 108', ' 394', ' 123', '2'], ['6628', '154', '371', ' 107', ' 395', ' 123', '2'], ['6630', '154', '371', ' 108', ' 395', ' 123', '2'], ['6631', '154', '371', ' 108', ' 396', ' 124', '2'], ['6632', '154', '371', ' 108', ' 397', ' 125', '2'], ['6633', '154', '371', ' 108', ' 397', ' 125', '2'], ['6634', '154', '371', ' 108', ' 398', ' 125', '2'], ['6635', '154', '371', ' 109', ' 398', ' 126', '2'], ['6636', '154', '372', ' 109', ' 398', ' 126', '2'], ['6637', '154', '372', ' 109', ' 398', ' 126', '2'], ['6638', '154', '372', ' 109', ' 399', ' 126', '2'], ['6639', '154', '373', ' 110', ' 399', ' 127', '2'], ['6640', '154', '373', ' 110', ' 400', ' 127', '2'], ['6641', '154', '373', ' 110', ' 400', ' 127', '2'], ['6642', '154', '373', ' 110', ' 400', ' 127', '2'], ['6646', '154', '373', ' 110', ' 401', ' 127', '2'], ['6655', '154', '376', ' 115', ' 404', ' 132', '2'], ['6656', '154', '378', ' 116', ' 404', ' 133', '2'], ['6659', '154', '377', ' 116', ' 406', ' 134', '2'], ['6660', '154', '378', ' 116', ' 406', ' 134', '2'], ['6661', '154', '378', ' 117', ' 406', ' 134', '2'], ['6663', '154', '379', ' 116', ' 408', ' 135', '2'], ['6664', '154', '377', ' 114', ' 409', ' 135', '2'], ['6665', '154', '377', ' 115', ' 410', ' 136', '2'], ['6666', '154', '378', ' 115', ' 411', ' 137', '2'], ['6667', '154', '378', ' 115', ' 411', ' 137', '2'], ['6668', '154', '379', ' 115', ' 411', ' 138', '2'], ['6669', '154', '379', ' 117', ' 411', ' 138', '2'], ['6670', '154', '380', ' 117', ' 411', ' 139', '2'], ['6671', '154', '381', ' 118', ' 411', ' 139', '2'], ['6672', '154', '382', ' 118', ' 412', ' 139', '2'], ['6673', '154', '382', ' 118', ' 412', ' 140', '2'], ['6674', '154', '383', ' 119', ' 412', ' 140', '2'], ['6675', '154', '384', ' 120', ' 412', ' 140', '2'], ['6676', '154', '384', ' 120', ' 413', ' 140', '2'], ['6677', '154', '384', ' 118', ' 415', ' 141', '2'], ['6678', '154', '383', ' 118', ' 415', ' 141', '2'], ['6679', '154', '383', ' 118', ' 415', ' 142', '2'], ['6680', '154', '383', ' 119', ' 417', ' 143', '2'], ['6681', '154', '385', ' 121', ' 417', ' 144', '2'], ['6682', '154', '387', ' 123', ' 416', ' 145', '2'], ['6683', '154', '388', ' 126', ' 416', ' 145', '2'], ['6684', '154', '389', ' 127', ' 416', ' 146', '2'], ['6685', '154', '389', ' 127', ' 417', ' 147', '2'], ['6686', '154', '388', ' 126', ' 418', ' 147', '2'], ['6687', '154', '389', ' 127', ' 417', ' 147', '2'], ['6688', '154', '389', ' 127', ' 419', ' 147', '2'], ['6689', '154', '390', ' 127', ' 420', ' 148', '2'], ['6690', '154', '389', ' 128', ' 421', ' 149', '2'], ['6691', '154', '389', ' 126', ' 422', ' 150', '2'], ['6692', '154', '389', ' 126', ' 423', ' 150', '2'], ['6693', '154', '390', ' 128', ' 424', ' 151', '2'], ['6694', '154', '388', ' 126', ' 425', ' 152', '2'], ['6695', '154', '389', ' 127', ' 426', ' 152', '2'], ['6696', '154', '389', ' 127', ' 427', ' 153', '2'], ['6697', '154', '390', ' 127', ' 428', ' 154', '2'], ['6698', '154', '390', ' 127', ' 428', ' 154', '2'], ['6699', '154', '391', ' 127', ' 430', ' 155', '2'], ['6700', '154', '392', ' 128', ' 430', ' 156', '2'], ['6701', '154', '393', ' 128', ' 432', ' 157', '2'], ['6702', '154', '392', ' 128', ' 432', ' 158', '2'], ['6703', '154', '393', ' 128', ' 432', ' 158', '2'], ['6704', '154', '393', ' 128', ' 434', ' 159', '2'], ['6705', '154', '393', ' 128', ' 435', ' 160', '2'], ['6706', '154', '395', ' 130', ' 436', ' 161', '2'], ['6707', '154', '396', ' 130', ' 437', ' 162', '2'], ['6708', '154', '396', ' 130', ' 439', ' 163', '2'], ['6709', '154', '396', ' 130', ' 440', ' 164', '2'], ['6710', '154', '397', ' 131', ' 440', ' 165', '2'], ['6711', '154', '397', ' 131', ' 442', ' 167', '2'], ['6712', '154', '398', ' 132', ' 442', ' 168', '2'], ['6713', '154', '398', ' 132', ' 444', ' 170', '2'], ['6714', '154', '398', ' 133', ' 444', ' 171', '2'], ['6715', '154', '400', ' 135', ' 444', ' 171', '2'], ['6716', '154', '400', ' 135', ' 445', ' 172', '2'], ['6717', '154', '403', ' 137', ' 445', ' 173', '2'], ['6718', '154', '403', ' 138', ' 446', ' 173', '2'], ['6719', '154', '404', ' 137', ' 448', ' 174', '2'], ['6720', '154', '405', ' 137', ' 449', ' 175', '2'], ['6721', '154', '405', ' 138', ' 451', ' 177', '2'], ['6722', '154', '406', ' 139', ' 451', ' 178', '2'], ['6723', '154', '406', ' 140', ' 454', ' 180', '2'], ['6724', '154', '408', ' 141', ' 456', ' 182', '2'], ['6725', '154', '409', ' 142', ' 457', ' 183', '2'], ['6726', '154', '410', ' 144', ' 458', ' 185', '2'], ['6727', '154', '411', ' 145', ' 459', ' 185', '2'], ['6728', '154', '412', ' 145', ' 460', ' 186', '2'], ['6729', '154', '412', ' 146', ' 462', ' 188', '2'], ['6730', '154', '414', ' 147', ' 463', ' 189', '2'], ['6731', '154', '414', ' 147', ' 464', ' 190', '2'], ['6732', '154', '416', ' 148', ' 466', ' 191', '2'], ['6733', '154', '416', ' 149', ' 467', ' 193', '2'], ['6734', '154', '417', ' 150', ' 469', ' 195', '2'], ['6735', '154', '418', ' 151', ' 471', ' 197', '2'], ['6736', '154', '419', ' 151', ' 472', ' 198', '2'], ['6738', '154', '421', ' 154', ' 475', ' 202', '2'], ['6739', '154', '423', ' 155', ' 478', ' 204', '2'], ['6740', '154', '424', ' 157', ' 479', ' 206', '2'], ['6741', '154', '426', ' 159', ' 481', ' 207', '2'], ['6742', '154', '426', ' 160', ' 483', ' 210', '2'], ['6743', '154', '427', ' 160', ' 485', ' 212', '2'], ['6744', '154', '428', ' 161', ' 487', ' 213', '2'], ['6745', '154', '429', ' 163', ' 490', ' 217', '2'], ['6746', '154', '431', ' 164', ' 493', ' 219', '2'], ['6747', '154', '432', ' 165', ' 494', ' 220', '2'], ['6748', '154', '433', ' 166', ' 496', ' 222', '2'], ['6749', '154', '434', ' 167', ' 498', ' 224', '2'], ['6750', '154', '435', ' 168', ' 501', ' 227', '2'], ['6751', '154', '437', ' 169', ' 504', ' 229', '2'], ['6752', '154', '438', ' 171', ' 507', ' 232', '2'], ['6753', '154', '441', ' 173', ' 510', ' 236', '2'], ['6754', '154', '444', ' 175', ' 512', ' 237', '2'], ['6755', '154', '445', ' 177', ' 516', ' 240', '2'], ['6756', '154', '446', ' 178', ' 520', ' 245', '2'], ['6757', '154', '448', ' 182', ' 522', ' 249', '2'], ['6758', '154', '450', ' 183', ' 526', ' 252', '2'], ['6759', '154', '451', ' 184', ' 529', ' 255', '2'], ['6760', '154', '455', ' 190', ' 531', ' 258', '2'], ['6761', '154', '457', ' 192', ' 535', ' 262', '2'], ['6762', '154', '459', ' 192', ' 540', ' 265', '2'], ['6763', '154', '459', ' 193', ' 545', ' 270', '2'], ['6764', '154', '462', ' 195', ' 551', ' 276', '2'], ['6765', '154', '464', ' 197', ' 554', ' 279', '2'], ['6766', '154', '467', ' 198', ' 556', ' 279', '2'], ['6767', '154', '469', ' 200', ' 562', ' 285', '2'], ['6768', '154', '472', ' 202', ' 567', ' 289', '2'], ['6769', '154', '474', ' 204', ' 571', ' 292', '2'], ['6770', '154', '478', ' 209', ' 577', ' 299', '2'], ['6771', '154', '481', ' 213', ' 583', ' 306', '2'], ['6773', '154', '487', ' 219', ' 592', ' 315', '2'], ['6774', '154', '491', ' 222', ' 600', ' 322', '2'], ['6775', '154', '494', ' 225', ' 607', ' 329', '2'], ['6777', '154', '500', ' 232', ' 619', ' 342', '2'], ['6778', '154', '506', ' 238', ' 627', ' 348', '2'], ['6779', '154', '511', ' 241', ' 637', ' 356', '2'], ['6780', '154', '515', ' 245', ' 645', ' 365', '2'], ['6781', '154', '520', ' 250', ' 654', ' 373', '2'], ['6782', '154', '524', ' 253', ' 664', ' 382', '2'], ['6783', '154', '528', ' 258', ' 675', ' 394', '2'], ['6784', '154', '533', ' 264', ' 685', ' 405', '2'], ['6785', '154', '540', ' 269', ' 694', ' 412', '2'], ['6786', '154', '550', ' 276', ' 702', ' 416', '2'], ['6787', '154', '562', ' 281', ' 712', ' 417', '2'], ['6788', '154', '571', ' 288', ' 718', ' 418', '2'], ['6789', '154', '580', ' 295', ' 720', ' 416', '2'], ['6790', '154', '589', ' 302', ' 722', ' 413', '2'], ['6791', '154', '600', ' 310', ' 729', ' 415', '2'], ['6792', '154', '611', ' 318', ' 735', ' 413', '2'], ['6793', '154', '621', ' 325', ' 741', ' 413', '2'], ['6794', '154', '631', ' 336', ' 746', ' 415', '2'], ['6795', '154', '641', ' 344', ' 746', ' 412', '2']], '166': [['7644', '166', '380', ' 108', ' 404', ' 126', '2'], ['7645', '166', '380', ' 108', ' 404', ' 127', '2'], ['7646', '166', '380', ' 108', ' 405', ' 127', '2'], ['7647', '166', '381', ' 108', ' 405', ' 128', '2'], ['7648', '166', '381', ' 109', ' 406', ' 128', '2'], ['7649', '166', '381', ' 109', ' 406', ' 129', '2'], ['7650', '166', '382', ' 110', ' 405', ' 128', '2'], ['7651', '166', '382', ' 111', ' 405', ' 128', '2'], ['7652', '166', '382', ' 111', ' 405', ' 128', '2'], ['7653', '166', '382', ' 111', ' 404', ' 128', '2'], ['7658', '166', '382', ' 111', ' 405', ' 128', '2'], ['7682', '166', '386', ' 115', ' 409', ' 133', '2'], ['7687', '166', '386', ' 116', ' 411', ' 136', '2'], ['7688', '166', '386', ' 116', ' 412', ' 136', '2'], ['7689', '166', '385', ' 115', ' 413', ' 137', '2'], ['7691', '166', '385', ' 115', ' 414', ' 138', '2'], ['7692', '166', '385', ' 115', ' 414', ' 139', '2'], ['7693', '166', '386', ' 115', ' 415', ' 139', '2'], ['7694', '166', '386', ' 115', ' 415', ' 139', '2'], ['7695', '166', '386', ' 115', ' 415', ' 139', '2'], ['7696', '166', '387', ' 116', ' 414', ' 140', '2'], ['7697', '166', '387', ' 116', ' 414', ' 140', '2'], ['7698', '166', '387', ' 117', ' 414', ' 140', '2'], ['7699', '166', '388', ' 117', ' 415', ' 140', '2'], ['7700', '166', '389', ' 118', ' 415', ' 140', '2'], ['7701', '166', '390', ' 120', ' 415', ' 141', '2'], ['7702', '166', '390', ' 120', ' 416', ' 141', '2'], ['7703', '166', '390', ' 121', ' 416', ' 142', '2'], ['7704', '166', '390', ' 119', ' 417', ' 142', '2'], ['7705', '166', '390', ' 120', ' 418', ' 142', '2'], ['7706', '166', '390', ' 120', ' 418', ' 143', '2'], ['7707', '166', '390', ' 121', ' 419', ' 143', '2'], ['7708', '166', '390', ' 121', ' 419', ' 144', '2'], ['7709', '166', '390', ' 121', ' 420', ' 145', '2'], ['7710', '166', '390', ' 121', ' 420', ' 145', '2'], ['7711', '166', '390', ' 121', ' 420', ' 145', '2'], ['7712', '166', '390', ' 121', ' 420', ' 146', '2'], ['7713', '166', '390', ' 122', ' 421', ' 147', '2'], ['7714', '166', '391', ' 123', ' 421', ' 147', '2'], ['7715', '166', '392', ' 123', ' 421', ' 147', '2'], ['7716', '166', '393', ' 124', ' 421', ' 147', '2'], ['7717', '166', '393', ' 125', ' 421', ' 147', '2'], ['7718', '166', '394', ' 126', ' 422', ' 148', '2'], ['7719', '166', '394', ' 127', ' 422', ' 149', '2'], ['7720', '166', '394', ' 128', ' 423', ' 150', '2'], ['7721', '166', '394', ' 128', ' 424', ' 151', '2'], ['7722', '166', '394', ' 128', ' 425', ' 151', '2'], ['7723', '166', '394', ' 128', ' 425', ' 151', '2'], ['7724', '166', '395', ' 129', ' 425', ' 152', '2'], ['7725', '166', '396', ' 129', ' 426', ' 152', '2'], ['7726', '166', '396', ' 130', ' 426', ' 152', '2'], ['7727', '166', '396', ' 130', ' 426', ' 153', '2'], ['7728', '166', '396', ' 130', ' 427', ' 153', '2'], ['7729', '166', '397', ' 130', ' 428', ' 153', '2'], ['7730', '166', '397', ' 131', ' 429', ' 154', '2'], ['7731', '166', '397', ' 131', ' 429', ' 155', '2'], ['7732', '166', '397', ' 131', ' 431', ' 156', '2'], ['7733', '166', '398', ' 132', ' 432', ' 157', '2'], ['7734', '166', '398', ' 132', ' 434', ' 158', '2'], ['7735', '166', '398', ' 132', ' 434', ' 159', '2'], ['7736', '166', '399', ' 133', ' 434', ' 159', '2'], ['7737', '166', '399', ' 134', ' 435', ' 160', '2'], ['7738', '166', '400', ' 134', ' 435', ' 160', '2'], ['7739', '166', '400', ' 134', ' 435', ' 160', '2'], ['7740', '166', '401', ' 135', ' 436', ' 161', '2'], ['7741', '166', '400', ' 135', ' 437', ' 162', '2'], ['7742', '166', '400', ' 134', ' 439', ' 163', '2'], ['7743', '166', '400', ' 134', ' 439', ' 164', '2'], ['7744', '166', '401', ' 135', ' 440', ' 164', '2'], ['7745', '166', '401', ' 136', ' 441', ' 165', '2'], ['7746', '166', '402', ' 136', ' 441', ' 166', '2'], ['7747', '166', '402', ' 136', ' 441', ' 166', '2'], ['7748', '166', '404', ' 138', ' 442', ' 166', '2'], ['7749', '166', '404', ' 138', ' 444', ' 168', '2'], ['7750', '166', '405', ' 138', ' 446', ' 169', '2'], ['7751', '166', '406', ' 139', ' 446', ' 170', '2'], ['7752', '166', '407', ' 140', ' 447', ' 170', '2'], ['7753', '166', '408', ' 141', ' 447', ' 171', '2'], ['7754', '166', '408', ' 142', ' 448', ' 172', '2'], ['7755', '166', '409', ' 143', ' 448', ' 173', '2'], ['7756', '166', '409', ' 143', ' 449', ' 174', '2'], ['7757', '166', '409', ' 143', ' 450', ' 174', '2'], ['7758', '166', '409', ' 143', ' 451', ' 175', '2'], ['7759', '166', '411', ' 145', ' 451', ' 176', '2'], ['7760', '166', '411', ' 145', ' 452', ' 177', '2'], ['7761', '166', '412', ' 146', ' 454', ' 178', '2'], ['7762', '166', '412', ' 146', ' 455', ' 179', '2'], ['7763', '166', '413', ' 147', ' 456', ' 180', '2'], ['7764', '166', '413', ' 148', ' 456', ' 181', '2'], ['7765', '166', '414', ' 149', ' 457', ' 182', '2'], ['7766', '166', '415', ' 149', ' 460', ' 184', '2'], ['7767', '166', '415', ' 149', ' 461', ' 185', '2'], ['7768', '166', '415', ' 149', ' 462', ' 186', '2'], ['7769', '166', '415', ' 149', ' 463', ' 187', '2'], ['7770', '166', '416', ' 150', ' 464', ' 188', '2'], ['7771', '166', '418', ' 151', ' 465', ' 189', '2'], ['7772', '166', '419', ' 152', ' 466', ' 190', '2'], ['7773', '166', '420', ' 152', ' 467', ' 190', '2'], ['7774', '166', '420', ' 153', ' 469', ' 193', '2'], ['7775', '166', '421', ' 154', ' 470', ' 194', '2'], ['7776', '166', '422', ' 156', ' 470', ' 196', '2'], ['7777', '166', '423', ' 157', ' 472', ' 197', '2'], ['7778', '166', '424', ' 158', ' 474', ' 199', '2'], ['7779', '166', '424', ' 158', ' 476', ' 201', '2'], ['7780', '166', '425', ' 159', ' 477', ' 202', '2'], ['7781', '166', '426', ' 160', ' 478', ' 204', '2'], ['7782', '166', '427', ' 161', ' 479', ' 204', '2'], ['7783', '166', '428', ' 162', ' 480', ' 205', '2'], ['7784', '166', '429', ' 163', ' 482', ' 207', '2'], ['7785', '166', '430', ' 165', ' 483', ' 209', '2'], ['7786', '166', '432', ' 166', ' 485', ' 211', '2'], ['7787', '166', '432', ' 167', ' 486', ' 213', '2'], ['7788', '166', '433', ' 168', ' 488', ' 215', '2'], ['7789', '166', '434', ' 169', ' 490', ' 216', '2'], ['7790', '166', '435', ' 170', ' 491', ' 217', '2'], ['7791', '166', '435', ' 171', ' 493', ' 220', '2'], ['7792', '166', '436', ' 173', ' 496', ' 224', '2'], ['7793', '166', '437', ' 174', ' 498', ' 226', '2'], ['7794', '166', '439', ' 177', ' 498', ' 228', '2'], ['7795', '166', '441', ' 179', ' 499', ' 228', '2'], ['7796', '166', '442', ' 181', ' 501', ' 230', '2'], ['7797', '166', '444', ' 183', ' 505', ' 234', '2'], ['7798', '166', '446', ' 184', ' 509', ' 237', '2'], ['7799', '166', '446', ' 186', ' 509', ' 239', '2'], ['7800', '166', '447', ' 187', ' 511', ' 241', '2'], ['7801', '166', '448', ' 190', ' 513', ' 243', '2'], ['7802', '166', '449', ' 192', ' 518', ' 249', '2'], ['7803', '166', '451', ' 192', ' 523', ' 251', '2'], ['7804', '166', '453', ' 194', ' 525', ' 254', '2'], ['7805', '166', '455', ' 197', ' 526', ' 256', '2'], ['7806', '166', '457', ' 198', ' 530', ' 259', '2'], ['7807', '166', '458', ' 200', ' 533', ' 262', '2'], ['7808', '166', '459', ' 202', ' 535', ' 265', '2'], ['7809', '166', '461', ' 204', ' 537', ' 267', '2'], ['7810', '166', '462', ' 206', ' 541', ' 270', '2'], ['7811', '166', '466', ' 209', ' 546', ' 275', '2'], ['7812', '166', '469', ' 212', ' 549', ' 277', '2'], ['7813', '166', '470', ' 215', ' 553', ' 282', '2'], ['7814', '166', '472', ' 218', ' 558', ' 288', '2'], ['7815', '166', '474', ' 219', ' 562', ' 291', '2'], ['7816', '166', '476', ' 222', ' 566', ' 295', '2'], ['7817', '166', '478', ' 224', ' 572', ' 300', '2'], ['7818', '166', '481', ' 229', ' 575', ' 304', '2'], ['7819', '166', '485', ' 231', ' 581', ' 308', '2'], ['7820', '166', '487', ' 235', ' 587', ' 315', '2'], ['7821', '166', '491', ' 239', ' 593', ' 321', '2'], ['7822', '166', '494', ' 243', ' 599', ' 327', '2'], ['7823', '166', '498', ' 248', ' 604', ' 332', '2'], ['7824', '166', '502', ' 251', ' 611', ' 338', '2'], ['7825', '166', '504', ' 254', ' 618', ' 345', '2'], ['7826', '166', '510', ' 259', ' 625', ' 352', '2'], ['7827', '166', '513', ' 263', ' 633', ' 359', '2'], ['7828', '166', '517', ' 269', ' 642', ' 368', '2'], ['7829', '166', '522', ' 274', ' 651', ' 376', '2'], ['7830', '166', '526', ' 278', ' 660', ' 386', '2'], ['7831', '166', '529', ' 284', ' 669', ' 397', '2'], ['7832', '166', '534', ' 290', ' 679', ' 407', '2'], ['7833', '166', '543', ' 296', ' 687', ' 411', '2'], ['7834', '166', '552', ' 302', ' 695', ' 414', '2'], ['7835', '166', '564', ' 310', ' 701', ' 416', '2'], ['7836', '166', '572', ' 317', ' 711', ' 421', '2'], ['7837', '166', '582', ' 323', ' 714', ' 419', '2'], ['7838', '166', '594', ' 328', ' 718', ' 414', '2'], ['7839', '166', '608', ' 339', ' 721', ' 413', '2'], ['7840', '166', '616', ' 347', ' 724', ' 413', '2'], ['7841', '166', '630', ' 357', ' 728', ' 413', '2']], '185': [['8698', '185', '337', ' 124', ' 377', ' 149', '2'], ['8699', '185', '336', ' 125', ' 378', ' 151', '2'], ['8700', '185', '336', ' 126', ' 378', ' 153', '2'], ['8702', '185', '336', ' 127', ' 378', ' 154', '2'], ['8707', '185', '335', ' 128', ' 378', ' 156', '2'], ['8708', '185', '336', ' 129', ' 379', ' 158', '2'], ['8709', '185', '336', ' 130', ' 379', ' 159', '2'], ['8712', '185', '336', ' 131', ' 379', ' 160', '2'], ['8713', '185', '336', ' 131', ' 381', ' 162', '2'], ['8714', '185', '338', ' 131', ' 386', ' 164', '2'], ['8715', '185', '337', ' 131', ' 384', ' 165', '2'], ['8716', '185', '336', ' 132', ' 383', ' 166', '2'], ['8717', '185', '336', ' 133', ' 382', ' 167', '2'], ['8718', '185', '339', ' 134', ' 387', ' 170', '2'], ['8719', '185', '337', ' 135', ' 386', ' 172', '2'], ['8721', '185', '337', ' 136', ' 385', ' 173', '2'], ['8722', '185', '337', ' 136', ' 385', ' 174', '2'], ['8723', '185', '337', ' 135', ' 387', ' 175', '2'], ['8724', '185', '337', ' 136', ' 387', ' 176', '2'], ['8725', '185', '338', ' 138', ' 385', ' 177', '2'], ['8726', '185', '337', ' 139', ' 385', ' 179', '2'], ['8727', '185', '337', ' 141', ' 384', ' 180', '2'], ['8728', '185', '338', ' 141', ' 384', ' 180', '2'], ['8729', '185', '338', ' 141', ' 385', ' 182', '2'], ['8730', '185', '339', ' 143', ' 384', ' 183', '2'], ['8731', '185', '340', ' 145', ' 385', ' 185', '2'], ['8732', '185', '340', ' 145', ' 386', ' 186', '2'], ['8733', '185', '340', ' 145', ' 386', ' 186', '2'], ['8734', '185', '341', ' 146', ' 386', ' 187', '2'], ['8735', '185', '341', ' 147', ' 386', ' 188', '2'], ['8736', '185', '341', ' 147', ' 386', ' 190', '2'], ['8737', '185', '340', ' 147', ' 388', ' 192', '2'], ['8738', '185', '340', ' 149', ' 387', ' 195', '2'], ['8739', '185', '341', ' 153', ' 387', ' 197', '2'], ['8740', '185', '341', ' 153', ' 388', ' 199', '2'], ['8741', '185', '341', ' 154', ' 389', ' 201', '2'], ['8742', '185', '341', ' 155', ' 389', ' 202', '2'], ['8743', '185', '343', ' 158', ' 389', ' 203', '2'], ['8744', '185', '342', ' 157', ' 391', ' 206', '2'], ['8745', '185', '342', ' 158', ' 392', ' 209', '2'], ['8746', '185', '342', ' 158', ' 393', ' 211', '2'], ['8747', '185', '342', ' 160', ' 393', ' 213', '2'], ['8748', '185', '343', ' 162', ' 393', ' 215', '2'], ['8749', '185', '343', ' 163', ' 393', ' 217', '2'], ['8750', '185', '342', ' 164', ' 394', ' 219', '2'], ['8751', '185', '342', ' 165', ' 395', ' 222', '2'], ['8752', '185', '341', ' 165', ' 396', ' 225', '2'], ['8753', '185', '341', ' 166', ' 397', ' 227', '2'], ['8754', '185', '341', ' 167', ' 398', ' 229', '2'], ['8755', '185', '341', ' 168', ' 398', ' 232', '2'], ['8756', '185', '342', ' 171', ' 399', ' 234', '2'], ['8757', '185', '342', ' 173', ' 400', ' 238', '2'], ['8758', '185', '343', ' 175', ' 402', ' 240', '2'], ['8759', '185', '343', ' 177', ' 404', ' 245', '2'], ['8760', '185', '342', ' 178', ' 406', ' 249', '2'], ['8761', '185', '343', ' 182', ' 407', ' 252', '2'], ['8762', '185', '343', ' 184', ' 409', ' 257', '2'], ['8763', '185', '342', ' 185', ' 411', ' 261', '2'], ['8764', '185', '343', ' 190', ' 411', ' 264', '2'], ['8765', '185', '341', ' 190', ' 412', ' 269', '2'], ['8766', '185', '342', ' 195', ' 413', ' 274', '2'], ['8767', '185', '341', ' 196', ' 415', ' 277', '2'], ['8768', '185', '342', ' 198', ' 417', ' 281', '2'], ['8769', '185', '342', ' 201', ' 418', ' 284', '2'], ['8770', '185', '342', ' 203', ' 421', ' 290', '2'], ['8771', '185', '342', ' 206', ' 425', ' 297', '2'], ['8772', '185', '342', ' 208', ' 426', ' 300', '2'], ['8773', '185', '342', ' 213', ' 427', ' 307', '2'], ['8774', '185', '342', ' 216', ' 429', ' 312', '2'], ['8775', '185', '343', ' 219', ' 433', ' 319', '2'], ['8776', '185', '344', ' 223', ' 436', ' 324', '2'], ['8777', '185', '343', ' 226', ' 438', ' 330', '2'], ['8778', '185', '344', ' 229', ' 442', ' 337', '2'], ['8779', '185', '343', ' 233', ' 445', ' 347', '2'], ['8780', '185', '344', ' 239', ' 447', ' 354', '2'], ['8781', '185', '343', ' 242', ' 450', ' 361', '2'], ['8782', '185', '343', ' 247', ' 454', ' 371', '2'], ['8786', '185', '344', ' 262', ' 466', ' 398', '2'], ['8787', '185', '346', ' 271', ' 471', ' 409', '2'], ['8788', '185', '350', ' 280', ' 473', ' 415', '2'], ['8789', '185', '356', ' 287', ' 475', ' 415', '2'], ['8794', '185', '373', ' 315', ' 470', ' 414', '2'], ['8795', '185', '383', ' 336', ' 467', ' 415', '2']], '190': [['8924', '190', '368', ' 107', ' 391', ' 120', '2'], ['8925', '190', '368', ' 108', ' 391', ' 121', '2'], ['8932', '190', '368', ' 108', ' 393', ' 121', '2'], ['8939', '190', '370', ' 110', ' 396', ' 124', '2'], ['8940', '190', '371', ' 110', ' 396', ' 125', '2'], ['8941', '190', '371', ' 111', ' 398', ' 126', '2'], ['8942', '190', '371', ' 110', ' 399', ' 126', '2'], ['8943', '190', '371', ' 110', ' 399', ' 126', '2'], ['8944', '190', '370', ' 109', ' 399', ' 126', '2'], ['8945', '190', '370', ' 109', ' 400', ' 126', '2'], ['8946', '190', '371', ' 109', ' 400', ' 126', '2'], ['8947', '190', '372', ' 109', ' 401', ' 127', '2'], ['8948', '190', '372', ' 110', ' 401', ' 127', '2'], ['8949', '190', '373', ' 110', ' 401', ' 127', '2'], ['8950', '190', '373', ' 110', ' 401', ' 127', '2'], ['8951', '190', '374', ' 110', ' 401', ' 127', '2'], ['8952', '190', '374', ' 110', ' 401', ' 127', '2'], ['8953', '190', '374', ' 110', ' 401', ' 127', '2'], ['8954', '190', '374', ' 110', ' 401', ' 127', '2'], ['8955', '190', '374', ' 110', ' 402', ' 127', '2'], ['8956', '190', '374', ' 110', ' 402', ' 128', '2'], ['8957', '190', '374', ' 110', ' 402', ' 128', '2'], ['8958', '190', '374', ' 110', ' 403', ' 129', '2'], ['8959', '190', '375', ' 110', ' 403', ' 129', '2'], ['8960', '190', '377', ' 113', ' 402', ' 130', '2'], ['8961', '190', '377', ' 113', ' 403', ' 131', '2'], ['8962', '190', '377', ' 112', ' 405', ' 131', '2'], ['8963', '190', '377', ' 113', ' 405', ' 132', '2'], ['8964', '190', '378', ' 113', ' 406', ' 132', '2'], ['8965', '190', '378', ' 113', ' 405', ' 132', '2'], ['8966', '190', '378', ' 113', ' 405', ' 132', '2'], ['8967', '190', '379', ' 115', ' 405', ' 133', '2'], ['8968', '190', '379', ' 115', ' 406', ' 133', '2'], ['8969', '190', '379', ' 114', ' 406', ' 133', '2'], ['8970', '190', '379', ' 114', ' 407', ' 133', '2'], ['8971', '190', '379', ' 114', ' 407', ' 133', '2'], ['8972', '190', '380', ' 115', ' 406', ' 134', '2'], ['8973', '190', '380', ' 115', ' 408', ' 134', '2'], ['8974', '190', '380', ' 114', ' 408', ' 134', '2'], ['8975', '190', '380', ' 114', ' 408', ' 135', '2'], ['8976', '190', '381', ' 114', ' 409', ' 134', '2'], ['8977', '190', '381', ' 114', ' 409', ' 134', '2'], ['8978', '190', '381', ' 113', ' 410', ' 134', '2'], ['8979', '190', '381', ' 113', ' 410', ' 135', '2'], ['8980', '190', '380', ' 114', ' 410', ' 136', '2'], ['8981', '190', '381', ' 115', ' 410', ' 136', '2'], ['8982', '190', '382', ' 116', ' 410', ' 137', '2'], ['8983', '190', '382', ' 116', ' 411', ' 137', '2'], ['8984', '190', '383', ' 116', ' 411', ' 138', '2'], ['8985', '190', '384', ' 117', ' 412', ' 138', '2'], ['8986', '190', '384', ' 117', ' 412', ' 138', '2'], ['8987', '190', '385', ' 118', ' 413', ' 139', '2'], ['8988', '190', '385', ' 118', ' 414', ' 139', '2'], ['8989', '190', '385', ' 117', ' 415', ' 139', '2'], ['8990', '190', '386', ' 119', ' 415', ' 140', '2'], ['8991', '190', '387', ' 118', ' 416', ' 140', '2'], ['8992', '190', '388', ' 119', ' 417', ' 141', '2'], ['8993', '190', '388', ' 119', ' 416', ' 141', '2'], ['8994', '190', '389', ' 120', ' 417', ' 141', '2'], ['8995', '190', '389', ' 121', ' 417', ' 142', '2'], ['8996', '190', '389', ' 121', ' 418', ' 143', '2'], ['8997', '190', '389', ' 122', ' 419', ' 144', '2'], ['8998', '190', '389', ' 122', ' 419', ' 145', '2'], ['8999', '190', '389', ' 122', ' 420', ' 145', '2'], ['9000', '190', '390', ' 123', ' 420', ' 146', '2'], ['9001', '190', '390', ' 122', ' 422', ' 146', '2'], ['9002', '190', '390', ' 122', ' 422', ' 147', '2'], ['9003', '190', '390', ' 122', ' 423', ' 147', '2'], ['9004', '190', '392', ' 123', ' 423', ' 147', '2'], ['9005', '190', '393', ' 124', ' 423', ' 147', '2'], ['9006', '190', '393', ' 125', ' 423', ' 148', '2'], ['9007', '190', '394', ' 126', ' 424', ' 148', '2'], ['9008', '190', '394', ' 127', ' 425', ' 149', '2'], ['9009', '190', '395', ' 127', ' 426', ' 150', '2'], ['9010', '190', '395', ' 127', ' 427', ' 150', '2'], ['9011', '190', '395', ' 127', ' 428', ' 151', '2'], ['9012', '190', '395', ' 128', ' 428', ' 152', '2'], ['9013', '190', '396', ' 129', ' 427', ' 152', '2'], ['9014', '190', '397', ' 130', ' 428', ' 152', '2'], ['9015', '190', '397', ' 130', ' 429', ' 153', '2'], ['9016', '190', '397', ' 130', ' 430', ' 154', '2'], ['9017', '190', '398', ' 130', ' 432', ' 155', '2'], ['9018', '190', '398', ' 130', ' 433', ' 155', '2'], ['9019', '190', '398', ' 130', ' 435', ' 157', '2'], ['9020', '190', '398', ' 131', ' 435', ' 157', '2'], ['9021', '190', '399', ' 131', ' 435', ' 158', '2'], ['9022', '190', '399', ' 132', ' 436', ' 158', '2'], ['9023', '190', '400', ' 132', ' 436', ' 158', '2'], ['9024', '190', '400', ' 132', ' 437', ' 159', '2'], ['9025', '190', '401', ' 133', ' 437', ' 159', '2'], ['9026', '190', '401', ' 134', ' 437', ' 160', '2'], ['9027', '190', '401', ' 133', ' 439', ' 160', '2'], ['9028', '190', '403', ' 134', ' 440', ' 161', '2'], ['9029', '190', '403', ' 134', ' 442', ' 162', '2'], ['9030', '190', '404', ' 135', ' 444', ' 163', '2'], ['9031', '190', '404', ' 135', ' 445', ' 164', '2'], ['9032', '190', '404', ' 136', ' 444', ' 165', '2'], ['9033', '190', '406', ' 137', ' 446', ' 165', '2'], ['9034', '190', '406', ' 138', ' 446', ' 166', '2'], ['9035', '190', '406', ' 138', ' 447', ' 167', '2'], ['9036', '190', '407', ' 139', ' 449', ' 168', '2'], ['9037', '190', '408', ' 139', ' 450', ' 169', '2'], ['9038', '190', '408', ' 140', ' 450', ' 170', '2'], ['9039', '190', '409', ' 141', ' 451', ' 171', '2'], ['9040', '190', '409', ' 141', ' 452', ' 172', '2'], ['9041', '190', '410', ' 141', ' 451', ' 172', '2'], ['9042', '190', '411', ' 142', ' 452', ' 172', '2'], ['9043', '190', '412', ' 143', ' 453', ' 173', '2'], ['9044', '190', '412', ' 144', ' 454', ' 174', '2'], ['9045', '190', '413', ' 144', ' 456', ' 175', '2'], ['9046', '190', '415', ' 145', ' 458', ' 177', '2'], ['9047', '190', '415', ' 146', ' 459', ' 178', '2'], ['9048', '190', '416', ' 146', ' 460', ' 179', '2'], ['9049', '190', '416', ' 146', ' 461', ' 180', '2'], ['9050', '190', '416', ' 147', ' 462', ' 181', '2'], ['9051', '190', '417', ' 148', ' 463', ' 183', '2'], ['9052', '190', '418', ' 149', ' 464', ' 184', '2'], ['9053', '190', '418', ' 149', ' 465', ' 184', '2'], ['9054', '190', '419', ' 149', ' 466', ' 185', '2'], ['9055', '190', '421', ' 152', ' 465', ' 185', '2'], ['9056', '190', '420', ' 152', ' 466', ' 187', '2'], ['9057', '190', '420', ' 152', ' 468', ' 189', '2'], ['9058', '190', '422', ' 153', ' 469', ' 190', '2'], ['9059', '190', '424', ' 156', ' 469', ' 191', '2'], ['9060', '190', '423', ' 156', ' 470', ' 192', '2'], ['9061', '190', '424', ' 157', ' 472', ' 195', '2'], ['9062', '190', '425', ' 157', ' 474', ' 196', '2'], ['9063', '190', '427', ' 159', ' 475', ' 197', '2'], ['9064', '190', '427', ' 159', ' 478', ' 199', '2'], ['9065', '190', '427', ' 159', ' 479', ' 200', '2'], ['9066', '190', '429', ' 160', ' 481', ' 202', '2'], ['9067', '190', '429', ' 161', ' 479', ' 201', '2'], ['9068', '190', '429', ' 163', ' 481', ' 204', '2'], ['9069', '190', '431', ' 164', ' 483', ' 205', '2'], ['9070', '190', '431', ' 165', ' 484', ' 207', '2'], ['9071', '190', '430', ' 165', ' 485', ' 209', '2'], ['9072', '190', '432', ' 166', ' 487', ' 210', '2'], ['9073', '190', '431', ' 166', ' 488', ' 211', '2'], ['9074', '190', '433', ' 167', ' 490', ' 213', '2'], ['9075', '190', '433', ' 168', ' 491', ' 215', '2'], ['9076', '190', '434', ' 169', ' 493', ' 217', '2'], ['9077', '190', '435', ' 170', ' 493', ' 218', '2'], ['9078', '190', '435', ' 172', ' 495', ' 221', '2'], ['9079', '190', '437', ' 173', ' 497', ' 223', '2'], ['9080', '190', '439', ' 175', ' 498', ' 225', '2'], ['9081', '190', '440', ' 177', ' 499', ' 226', '2'], ['9082', '190', '442', ' 178', ' 501', ' 227', '2'], ['9083', '190', '443', ' 179', ' 503', ' 229', '2'], ['9084', '190', '442', ' 180', ' 506', ' 233', '2'], ['9085', '190', '444', ' 183', ' 507', ' 236', '2'], ['9086', '190', '445', ' 185', ' 508', ' 238', '2'], ['9087', '190', '445', ' 186', ' 510', ' 240', '2'], ['9088', '190', '448', ' 189', ' 512', ' 242', '2'], ['9089', '190', '449', ' 190', ' 514', ' 245', '2'], ['9090', '190', '451', ' 192', ' 517', ' 247', '2'], ['9091', '190', '452', ' 194', ' 519', ' 250', '2'], ['9092', '190', '452', ' 196', ' 521', ' 253', '2'], ['9093', '190', '453', ' 197', ' 524', ' 256', '2'], ['9094', '190', '454', ' 198', ' 527', ' 258', '2'], ['9095', '190', '455', ' 199', ' 529', ' 261', '2'], ['9096', '190', '457', ' 200', ' 531', ' 262', '2'], ['9097', '190', '458', ' 202', ' 533', ' 266', '2'], ['9098', '190', '458', ' 203', ' 538', ' 271', '2'], ['9099', '190', '459', ' 204', ' 541', ' 274', '2'], ['9100', '190', '462', ' 208', ' 543', ' 277', '2'], ['9101', '190', '464', ' 211', ' 545', ' 280', '2'], ['9102', '190', '465', ' 214', ' 548', ' 285', '2'], ['9103', '190', '468', ' 216', ' 552', ' 288', '2'], ['9104', '190', '469', ' 218', ' 556', ' 293', '2'], ['9105', '190', '470', ' 221', ' 558', ' 297', '2'], ['9106', '190', '473', ' 224', ' 561', ' 300', '2'], ['9107', '190', '474', ' 225', ' 565', ' 304', '2'], ['9108', '190', '476', ' 229', ' 569', ' 310', '2'], ['9109', '190', '479', ' 232', ' 573', ' 313', '2'], ['9110', '190', '481', ' 235', ' 577', ' 319', '2'], ['9111', '190', '484', ' 239', ' 582', ' 325', '2'], ['9112', '190', '487', ' 242', ' 587', ' 329', '2'], ['9113', '190', '489', ' 245', ' 591', ' 335', '2'], ['9114', '190', '490', ' 248', ' 596', ' 340', '2'], ['9115', '190', '493', ' 251', ' 601', ' 346', '2'], ['9116', '190', '496', ' 256', ' 605', ' 351', '2'], ['9117', '190', '499', ' 260', ' 610', ' 358', '2'], ['9118', '190', '502', ' 265', ' 615', ' 365', '2'], ['9119', '190', '505', ' 269', ' 622', ' 372', '2'], ['9120', '190', '508', ' 273', ' 629', ' 380', '2'], ['9121', '190', '511', ' 277', ' 636', ' 388', '2'], ['9122', '190', '514', ' 281', ' 645', ' 398', '2'], ['9123', '190', '518', ' 287', ' 651', ' 407', '2'], ['9124', '190', '523', ' 292', ' 656', ' 411', '2'], ['9125', '190', '530', ' 298', ' 660', ' 414', '2'], ['9126', '190', '538', ' 304', ' 663', ' 414', '2'], ['9127', '190', '548', ' 310', ' 671', ' 416', '2'], ['9128', '190', '554', ' 317', ' 673', ' 415', '2'], ['9129', '190', '560', ' 322', ' 672', ' 413', '2'], ['9130', '190', '567', ' 325', ' 678', ' 412', '2'], ['9131', '190', '577', ' 336', ' 681', ' 413', '2'], ['9132', '190', '591', ' 344', ' 691', ' 413', '2'], ['9133', '190', '600', ' 353', ' 694', ' 412', '2']], '242': [['10400', '242', '364', ' 106', ' 387', ' 120', '2'], ['10401', '242', '364', ' 106', ' 387', ' 120', '2'], ['10402', '242', '364', ' 106', ' 386', ' 120', '2'], ['10403', '242', '364', ' 106', ' 386', ' 120', '2'], ['10404', '242', '364', ' 106', ' 386', ' 120', '2'], ['10405', '242', '365', ' 106', ' 387', ' 120', '2'], ['10406', '242', '365', ' 107', ' 387', ' 121', '2'], ['10407', '242', '365', ' 107', ' 387', ' 121', '2'], ['10414', '242', '364', ' 107', ' 389', ' 122', '2'], ['10415', '242', '364', ' 107', ' 390', ' 123', '2'], ['10416', '242', '364', ' 107', ' 391', ' 123', '2'], ['10417', '242', '364', ' 107', ' 391', ' 124', '2'], ['10418', '242', '364', ' 107', ' 391', ' 125', '2'], ['10419', '242', '364', ' 107', ' 391', ' 125', '2'], ['10420', '242', '363', ' 107', ' 391', ' 125', '2'], ['10421', '242', '363', ' 107', ' 392', ' 126', '2'], ['10422', '242', '364', ' 107', ' 391', ' 126', '2'], ['10423', '242', '365', ' 108', ' 392', ' 126', '2'], ['10424', '242', '365', ' 108', ' 392', ' 127', '2'], ['10425', '242', '365', ' 109', ' 391', ' 127', '2'], ['10426', '242', '364', ' 109', ' 391', ' 127', '2'], ['10427', '242', '365', ' 109', ' 391', ' 127', '2'], ['10428', '242', '364', ' 109', ' 391', ' 127', '2'], ['10429', '242', '364', ' 109', ' 391', ' 127', '2'], ['10430', '242', '363', ' 109', ' 391', ' 128', '2'], ['10431', '242', '363', ' 109', ' 392', ' 129', '2'], ['10432', '242', '364', ' 110', ' 392', ' 129', '2'], ['10433', '242', '364', ' 112', ' 391', ' 130', '2'], ['10434', '242', '365', ' 112', ' 391', ' 131', '2'], ['10435', '242', '364', ' 112', ' 392', ' 131', '2'], ['10436', '242', '364', ' 112', ' 393', ' 131', '2'], ['10437', '242', '364', ' 113', ' 392', ' 132', '2'], ['10438', '242', '365', ' 115', ' 391', ' 132', '2'], ['10439', '242', '366', ' 117', ' 391', ' 133', '2'], ['10440', '242', '366', ' 118', ' 390', ' 134', '2'], ['10441', '242', '365', ' 117', ' 391', ' 134', '2'], ['10442', '242', '365', ' 117', ' 391', ' 134', '2'], ['10443', '242', '365', ' 116', ' 392', ' 134', '2'], ['10444', '242', '366', ' 118', ' 391', ' 134', '2'], ['10445', '242', '365', ' 118', ' 392', ' 135', '2'], ['10446', '242', '366', ' 118', ' 392', ' 135', '2'], ['10447', '242', '365', ' 118', ' 393', ' 135', '2'], ['10448', '242', '365', ' 118', ' 393', ' 136', '2'], ['10449', '242', '364', ' 117', ' 394', ' 137', '2'], ['10450', '242', '364', ' 117', ' 394', ' 137', '2'], ['10451', '242', '364', ' 117', ' 397', ' 139', '2'], ['10452', '242', '366', ' 119', ' 396', ' 139', '2'], ['10453', '242', '366', ' 120', ' 395', ' 140', '2'], ['10454', '242', '365', ' 119', ' 396', ' 140', '2'], ['10455', '242', '363', ' 118', ' 397', ' 141', '2'], ['10456', '242', '361', ' 114', ' 400', ' 142', '2'], ['10457', '242', '359', ' 112', ' 401', ' 143', '2'], ['10458', '242', '360', ' 113', ' 401', ' 143', '2'], ['10459', '242', '361', ' 115', ' 400', ' 144', '2'], ['10460', '242', '361', ' 115', ' 399', ' 145', '2'], ['10461', '242', '361', ' 115', ' 399', ' 145', '2'], ['10462', '242', '361', ' 116', ' 399', ' 146', '2'], ['10463', '242', '362', ' 116', ' 400', ' 146', '2'], ['10464', '242', '363', ' 117', ' 399', ' 147', '2'], ['10465', '242', '364', ' 119', ' 398', ' 147', '2'], ['10466', '242', '366', ' 121', ' 398', ' 148', '2'], ['10467', '242', '365', ' 121', ' 399', ' 150', '2'], ['10468', '242', '364', ' 121', ' 399', ' 150', '2'], ['10469', '242', '365', ' 122', ' 399', ' 151', '2'], ['10470', '242', '366', ' 125', ' 398', ' 152', '2'], ['10471', '242', '366', ' 126', ' 397', ' 152', '2'], ['10472', '242', '366', ' 126', ' 397', ' 152', '2'], ['10473', '242', '366', ' 127', ' 398', ' 153', '2'], ['10474', '242', '366', ' 127', ' 399', ' 154', '2'], ['10475', '242', '366', ' 127', ' 399', ' 154', '2'], ['10477', '242', '365', ' 127', ' 401', ' 157', '2'], ['10478', '242', '366', ' 129', ' 400', ' 157', '2'], ['10480', '242', '365', ' 129', ' 402', ' 160', '2'], ['10481', '242', '366', ' 129', ' 403', ' 161', '2'], ['10482', '242', '365', ' 130', ' 403', ' 163', '2'], ['10483', '242', '365', ' 130', ' 404', ' 164', '2'], ['10484', '242', '365', ' 131', ' 405', ' 165', '2'], ['10485', '242', '365', ' 132', ' 405', ' 167', '2'], ['10486', '242', '366', ' 133', ' 406', ' 169', '2'], ['10487', '242', '366', ' 134', ' 406', ' 170', '2'], ['10488', '242', '366', ' 135', ' 406', ' 171', '2'], ['10489', '242', '366', ' 136', ' 406', ' 172', '2'], ['10490', '242', '367', ' 136', ' 407', ' 173', '2'], ['10491', '242', '366', ' 136', ' 408', ' 174', '2'], ['10492', '242', '367', ' 136', ' 409', ' 176', '2'], ['10493', '242', '367', ' 137', ' 410', ' 177', '2'], ['10494', '242', '367', ' 138', ' 411', ' 179', '2'], ['10495', '242', '367', ' 140', ' 410', ' 180', '2'], ['10496', '242', '367', ' 140', ' 410', ' 182', '2'], ['10497', '242', '367', ' 142', ' 411', ' 184', '2'], ['10498', '242', '368', ' 142', ' 411', ' 184', '2'], ['10499', '242', '368', ' 143', ' 411', ' 185', '2'], ['10500', '242', '368', ' 144', ' 413', ' 187', '2'], ['10501', '242', '369', ' 147', ' 414', ' 190', '2'], ['10502', '242', '370', ' 148', ' 414', ' 191', '2'], ['10503', '242', '370', ' 149', ' 416', ' 193', '2'], ['10504', '242', '370', ' 149', ' 417', ' 195', '2'], ['10505', '242', '370', ' 150', ' 418', ' 197', '2'], ['10506', '242', '370', ' 151', ' 419', ' 199', '2'], ['10507', '242', '371', ' 154', ' 420', ' 202', '2'], ['10508', '242', '372', ' 156', ' 421', ' 204', '2'], ['10509', '242', '372', ' 158', ' 421', ' 206', '2'], ['10510', '242', '373', ' 160', ' 423', ' 208', '2'], ['10511', '242', '373', ' 160', ' 424', ' 210', '2'], ['10512', '242', '373', ' 162', ' 426', ' 212', '2'], ['10513', '242', '373', ' 162', ' 427', ' 215', '2'], ['10514', '242', '374', ' 163', ' 429', ' 218', '2'], ['10515', '242', '373', ' 164', ' 429', ' 220', '2'], ['10516', '242', '373', ' 167', ' 431', ' 224', '2'], ['10517', '242', '373', ' 167', ' 432', ' 226', '2'], ['10518', '242', '374', ' 168', ' 434', ' 228', '2'], ['10519', '242', '375', ' 169', ' 436', ' 231', '2'], ['10520', '242', '375', ' 171', ' 438', ' 235', '2'], ['10521', '242', '376', ' 172', ' 440', ' 238', '2'], ['10522', '242', '376', ' 174', ' 443', ' 243', '2'], ['10523', '242', '376', ' 177', ' 444', ' 247', '2'], ['10524', '242', '377', ' 179', ' 446', ' 250', '2'], ['10525', '242', '378', ' 182', ' 447', ' 253', '2'], ['10526', '242', '378', ' 183', ' 448', ' 256', '2'], ['10527', '242', '379', ' 186', ' 452', ' 262', '2'], ['10528', '242', '379', ' 188', ' 454', ' 266', '2'], ['10529', '242', '380', ' 190', ' 456', ' 271', '2'], ['10530', '242', '381', ' 193', ' 457', ' 274', '2'], ['10531', '242', '381', ' 196', ' 460', ' 281', '2'], ['10532', '242', '381', ' 199', ' 463', ' 287', '2'], ['10533', '242', '383', ' 203', ' 466', ' 293', '2'], ['10534', '242', '384', ' 205', ' 469', ' 297', '2'], ['10535', '242', '386', ' 209', ' 472', ' 302', '2'], ['10536', '242', '387', ' 213', ' 476', ' 308', '2'], ['10537', '242', '388', ' 217', ' 481', ' 317', '2'], ['10538', '242', '389', ' 221', ' 485', ' 324', '2'], ['10539', '242', '390', ' 224', ' 489', ' 331', '2'], ['10540', '242', '392', ' 228', ' 493', ' 337', '2'], ['10541', '242', '393', ' 232', ' 499', ' 346', '2'], ['10542', '242', '395', ' 238', ' 502', ' 353', '2'], ['10543', '242', '396', ' 242', ' 509', ' 362', '2'], ['10544', '242', '397', ' 246', ' 514', ' 373', '2'], ['10545', '242', '398', ' 250', ' 521', ' 383', '2'], ['10546', '242', '397', ' 256', ' 530', ' 400', '2'], ['10547', '242', '401', ' 263', ' 536', ' 409', '2'], ['10548', '242', '406', ' 269', ' 540', ' 413', '2'], ['10549', '242', '412', ' 275', ' 543', ' 415', '2'], ['10550', '242', '417', ' 281', ' 548', ' 417', '2'], ['10551', '242', '427', ' 290', ' 539', ' 402', '2'], ['10552', '242', '434', ' 298', ' 545', ' 405', '2'], ['10553', '242', '438', ' 306', ' 551', ' 412', '2'], ['10554', '242', '446', ' 316', ' 557', ' 414', '2'], ['10555', '242', '451', ' 324', ' 556', ' 413', '2']], '256': [['10641', '256', '369', ' 106', ' 391', ' 120', '2'], ['10642', '256', '369', ' 106', ' 391', ' 120', '2'], ['10644', '256', '369', ' 106', ' 391', ' 120', '2'], ['10645', '256', '370', ' 107', ' 392', ' 121', '2'], ['10646', '256', '371', ' 108', ' 392', ' 122', '2'], ['10647', '256', '371', ' 109', ' 392', ' 122', '2'], ['10648', '256', '371', ' 109', ' 392', ' 122', '2'], ['10649', '256', '371', ' 108', ' 393', ' 122', '2'], ['10650', '256', '371', ' 108', ' 394', ' 122', '2'], ['10651', '256', '371', ' 108', ' 395', ' 123', '2'], ['10652', '256', '371', ' 109', ' 396', ' 124', '2'], ['10653', '256', '372', ' 109', ' 397', ' 125', '2'], ['10654', '256', '372', ' 109', ' 397', ' 126', '2'], ['10655', '256', '372', ' 110', ' 397', ' 126', '2'], ['10656', '256', '372', ' 108', ' 398', ' 126', '2'], ['10657', '256', '372', ' 108', ' 400', ' 126', '2'], ['10658', '256', '372', ' 108', ' 401', ' 127', '2'], ['10659', '256', '372', ' 108', ' 401', ' 127', '2'], ['10660', '256', '373', ' 108', ' 401', ' 127', '2'], ['10661', '256', '372', ' 108', ' 401', ' 128', '2'], ['10662', '256', '373', ' 108', ' 402', ' 129', '2'], ['10663', '256', '373', ' 109', ' 402', ' 129', '2'], ['10664', '256', '374', ' 110', ' 403', ' 130', '2'], ['10665', '256', '375', ' 112', ' 402', ' 131', '2'], ['10666', '256', '376', ' 113', ' 402', ' 132', '2'], ['10667', '256', '377', ' 115', ' 402', ' 132', '2'], ['10668', '256', '379', ' 118', ' 403', ' 133', '2'], ['10669', '256', '380', ' 118', ' 403', ' 134', '2'], ['10670', '256', '378', ' 117', ' 405', ' 134', '2'], ['10671', '256', '378', ' 117', ' 406', ' 135', '2'], ['10672', '256', '378', ' 118', ' 406', ' 136', '2'], ['10673', '256', '379', ' 118', ' 408', ' 137', '2'], ['10674', '256', '379', ' 118', ' 409', ' 138', '2'], ['10675', '256', '379', ' 119', ' 409', ' 139', '2'], ['10676', '256', '379', ' 119', ' 410', ' 139', '2'], ['10677', '256', '380', ' 120', ' 410', ' 140', '2'], ['10678', '256', '379', ' 119', ' 412', ' 140', '2'], ['10679', '256', '379', ' 118', ' 413', ' 141', '2'], ['10680', '256', '380', ' 119', ' 413', ' 141', '2'], ['10681', '256', '380', ' 119', ' 413', ' 142', '2'], ['10682', '256', '380', ' 120', ' 414', ' 143', '2'], ['10683', '256', '380', ' 121', ' 414', ' 144', '2'], ['10684', '256', '380', ' 121', ' 414', ' 145', '2'], ['10685', '256', '381', ' 122', ' 415', ' 146', '2'], ['10686', '256', '384', ' 124', ' 416', ' 147', '2'], ['10687', '256', '383', ' 124', ' 417', ' 148', '2'], ['10688', '256', '384', ' 125', ' 419', ' 150', '2'], ['10689', '256', '384', ' 125', ' 420', ' 151', '2'], ['10690', '256', '385', ' 126', ' 421', ' 152', '2'], ['10691', '256', '385', ' 127', ' 422', ' 153', '2'], ['10692', '256', '385', ' 128', ' 422', ' 154', '2'], ['10693', '256', '386', ' 128', ' 424', ' 155', '2'], ['10694', '256', '387', ' 129', ' 424', ' 156', '2'], ['10695', '256', '387', ' 130', ' 424', ' 156', '2'], ['10696', '256', '387', ' 130', ' 425', ' 158', '2'], ['10697', '256', '387', ' 130', ' 427', ' 159', '2'], ['10698', '256', '388', ' 131', ' 427', ' 160', '2'], ['10699', '256', '389', ' 133', ' 428', ' 161', '2'], ['10700', '256', '390', ' 133', ' 429', ' 162', '2'], ['10701', '256', '392', ' 134', ' 433', ' 165', '2'], ['10702', '256', '392', ' 134', ' 435', ' 166', '2'], ['10703', '256', '392', ' 134', ' 435', ' 168', '2'], ['10704', '256', '392', ' 135', ' 437', ' 169', '2'], ['10705', '256', '393', ' 136', ' 438', ' 171', '2'], ['10706', '256', '394', ' 137', ' 440', ' 172', '2'], ['10707', '256', '395', ' 138', ' 441', ' 174', '2'], ['10708', '256', '396', ' 140', ' 441', ' 175', '2'], ['10709', '256', '398', ' 141', ' 441', ' 175', '2'], ['10710', '256', '398', ' 142', ' 443', ' 177', '2'], ['10711', '256', '399', ' 143', ' 445', ' 178', '2'], ['10712', '256', '400', ' 145', ' 446', ' 180', '2'], ['10713', '256', '401', ' 146', ' 448', ' 182', '2'], ['10714', '256', '402', ' 147', ' 449', ' 184', '2'], ['10715', '256', '402', ' 146', ' 452', ' 186', '2'], ['10716', '256', '403', ' 147', ' 454', ' 188', '2'], ['10717', '256', '404', ' 148', ' 456', ' 190', '2'], ['10718', '256', '407', ' 150', ' 457', ' 191', '2'], ['10719', '256', '409', ' 152', ' 460', ' 194', '2'], ['10720', '256', '409', ' 153', ' 462', ' 197', '2'], ['10721', '256', '411', ' 155', ' 464', ' 199', '2'], ['10722', '256', '412', ' 157', ' 466', ' 201', '2'], ['10723', '256', '413', ' 158', ' 467', ' 203', '2'], ['10724', '256', '414', ' 160', ' 469', ' 206', '2'], ['10725', '256', '415', ' 161', ' 470', ' 207', '2'], ['10726', '256', '416', ' 162', ' 473', ' 210', '2'], ['10727', '256', '418', ' 163', ' 475', ' 212', '2'], ['10728', '256', '419', ' 165', ' 477', ' 214', '2'], ['10729', '256', '421', ' 166', ' 481', ' 217', '2'], ['10730', '256', '422', ' 168', ' 484', ' 221', '2'], ['10731', '256', '423', ' 172', ' 486', ' 225', '2'], ['10732', '256', '425', ' 173', ' 487', ' 227', '2'], ['10733', '256', '428', ' 176', ' 491', ' 229', '2'], ['10734', '256', '429', ' 178', ' 494', ' 233', '2'], ['10735', '256', '430', ' 179', ' 498', ' 236', '2'], ['10736', '256', '432', ' 181', ' 500', ' 239', '2'], ['10737', '256', '433', ' 183', ' 504', ' 244', '2'], ['10738', '256', '436', ' 185', ' 507', ' 246', '2'], ['10739', '256', '438', ' 189', ' 510', ' 250', '2'], ['10740', '256', '439', ' 191', ' 514', ' 255', '2'], ['10741', '256', '440', ' 192', ' 520', ' 260', '2'], ['10742', '256', '442', ' 194', ' 523', ' 264', '2'], ['10743', '256', '443', ' 196', ' 528', ' 270', '2'], ['10744', '256', '447', ' 201', ' 532', ' 275', '2'], ['10745', '256', '450', ' 203', ' 536', ' 278', '2'], ['10746', '256', '452', ' 205', ' 541', ' 284', '2'], ['10747', '256', '455', ' 209', ' 546', ' 289', '2'], ['10748', '256', '458', ' 213', ' 551', ' 296', '2'], ['10749', '256', '462', ' 217', ' 556', ' 301', '2'], ['10750', '256', '464', ' 220', ' 562', ' 307', '2'], ['10751', '256', '468', ' 224', ' 568', ' 313', '2'], ['10752', '256', '471', ' 228', ' 575', ' 320', '2'], ['10753', '256', '474', ' 232', ' 581', ' 327', '2'], ['10754', '256', '478', ' 236', ' 588', ' 334', '2'], ['10755', '256', '482', ' 242', ' 594', ' 342', '2'], ['10756', '256', '486', ' 246', ' 602', ' 350', '2'], ['10757', '256', '490', ' 250', ' 610', ' 359', '2'], ['10758', '256', '494', ' 256', ' 619', ' 368', '2'], ['10759', '256', '500', ' 261', ' 628', ' 377', '2'], ['10760', '256', '505', ' 268', ' 638', ' 388', '2'], ['10761', '256', '509', ' 273', ' 649', ' 401', '2'], ['10762', '256', '515', ' 279', ' 658', ' 409', '2'], ['10763', '256', '523', ' 285', ' 665', ' 413', '2'], ['10764', '256', '536', ' 293', ' 674', ' 415', '2'], ['10765', '256', '545', ' 301', ' 680', ' 417', '2'], ['10766', '256', '565', ' 310', ' 695', ' 416', '2'], ['10767', '256', '569', ' 319', ' 689', ' 414', '2'], ['10768', '256', '578', ' 324', ' 698', ' 414', '2'], ['10769', '256', '592', ' 336', ' 703', ' 414', '2'], ['10770', '256', '601', ' 346', ' 702', ' 412', '2']], '267': [['11233', '267', '376', ' 106', ' 395', ' 121', '2'], ['11237', '267', '376', ' 107', ' 396', ' 121', '2'], ['11238', '267', '376', ' 107', ' 396', ' 122', '2'], ['11242', '267', '376', ' 106', ' 399', ' 123', '2'], ['11243', '267', '376', ' 107', ' 399', ' 124', '2'], ['11244', '267', '377', ' 107', ' 400', ' 125', '2'], ['11245', '267', '377', ' 108', ' 400', ' 126', '2'], ['11246', '267', '379', ' 108', ' 401', ' 126', '2'], ['11247', '267', '379', ' 108', ' 401', ' 126', '2'], ['11248', '267', '380', ' 109', ' 402', ' 126', '2'], ['11249', '267', '380', ' 109', ' 403', ' 127', '2'], ['11250', '267', '380', ' 107', ' 406', ' 127', '2'], ['11251', '267', '380', ' 107', ' 406', ' 128', '2'], ['11252', '267', '381', ' 107', ' 406', ' 127', '2'], ['11253', '267', '381', ' 107', ' 407', ' 128', '2'], ['11255', '267', '382', ' 108', ' 408', ' 129', '2'], ['11256', '267', '383', ' 108', ' 408', ' 129', '2'], ['11257', '267', '383', ' 108', ' 408', ' 129', '2'], ['11258', '267', '383', ' 109', ' 408', ' 129', '2'], ['11259', '267', '383', ' 108', ' 409', ' 129', '2'], ['11260', '267', '383', ' 108', ' 410', ' 130', '2'], ['11261', '267', '384', ' 109', ' 410', ' 131', '2'], ['11262', '267', '385', ' 111', ' 409', ' 131', '2'], ['11263', '267', '385', ' 112', ' 409', ' 131', '2'], ['11264', '267', '386', ' 112', ' 410', ' 132', '2'], ['11265', '267', '386', ' 113', ' 411', ' 132', '2'], ['11266', '267', '388', ' 114', ' 411', ' 133', '2'], ['11267', '267', '388', ' 115', ' 412', ' 133', '2'], ['11268', '267', '388', ' 113', ' 413', ' 134', '2'], ['11269', '267', '389', ' 114', ' 414', ' 134', '2'], ['11270', '267', '389', ' 114', ' 414', ' 134', '2'], ['11271', '267', '390', ' 114', ' 415', ' 134', '2'], ['11272', '267', '390', ' 114', ' 416', ' 134', '2'], ['11273', '267', '390', ' 114', ' 416', ' 134', '2'], ['11274', '267', '391', ' 114', ' 418', ' 135', '2'], ['11275', '267', '391', ' 115', ' 418', ' 136', '2'], ['11276', '267', '392', ' 115', ' 419', ' 137', '2'], ['11277', '267', '392', ' 116', ' 419', ' 138', '2'], ['11278', '267', '392', ' 116', ' 420', ' 138', '2'], ['11279', '267', '394', ' 118', ' 421', ' 139', '2'], ['11280', '267', '394', ' 118', ' 422', ' 140', '2'], ['11281', '267', '394', ' 117', ' 422', ' 140', '2'], ['11282', '267', '394', ' 117', ' 423', ' 140', '2'], ['11283', '267', '395', ' 117', ' 423', ' 140', '2'], ['11284', '267', '396', ' 117', ' 422', ' 139', '2'], ['11285', '267', '395', ' 118', ' 424', ' 141', '2'], ['11286', '267', '395', ' 118', ' 425', ' 142', '2'], ['11287', '267', '396', ' 118', ' 426', ' 142', '2'], ['11288', '267', '396', ' 117', ' 426', ' 143', '2'], ['11289', '267', '396', ' 117', ' 427', ' 143', '2'], ['11290', '267', '396', ' 117', ' 428', ' 145', '2'], ['11291', '267', '396', ' 117', ' 429', ' 146', '2'], ['11292', '267', '397', ' 118', ' 429', ' 146', '2'], ['11293', '267', '398', ' 118', ' 430', ' 147', '2'], ['11294', '267', '399', ' 119', ' 430', ' 147', '2'], ['11295', '267', '400', ' 120', ' 430', ' 147', '2'], ['11296', '267', '400', ' 120', ' 431', ' 148', '2'], ['11297', '267', '401', ' 120', ' 433', ' 149', '2'], ['11298', '267', '402', ' 121', ' 434', ' 150', '2'], ['11299', '267', '402', ' 121', ' 434', ' 150', '2'], ['11300', '267', '403', ' 122', ' 435', ' 151', '2'], ['11301', '267', '403', ' 123', ' 436', ' 152', '2'], ['11302', '267', '403', ' 123', ' 436', ' 153', '2'], ['11303', '267', '404', ' 123', ' 438', ' 154', '2'], ['11304', '267', '405', ' 123', ' 438', ' 154', '2'], ['11305', '267', '406', ' 124', ' 439', ' 155', '2'], ['11306', '267', '407', ' 126', ' 440', ' 156', '2'], ['11307', '267', '407', ' 126', ' 440', ' 156', '2'], ['11308', '267', '408', ' 127', ' 442', ' 158', '2'], ['11309', '267', '408', ' 127', ' 443', ' 159', '2'], ['11310', '267', '408', ' 127', ' 444', ' 160', '2'], ['11311', '267', '410', ' 128', ' 445', ' 161', '2'], ['11312', '267', '411', ' 129', ' 446', ' 161', '2'], ['11313', '267', '411', ' 129', ' 447', ' 162', '2'], ['11314', '267', '413', ' 130', ' 448', ' 163', '2'], ['11315', '267', '413', ' 131', ' 450', ' 164', '2'], ['11316', '267', '413', ' 130', ' 451', ' 165', '2'], ['11317', '267', '414', ' 131', ' 451', ' 166', '2'], ['11318', '267', '415', ' 131', ' 453', ' 166', '2'], ['11319', '267', '416', ' 131', ' 455', ' 168', '2'], ['11320', '267', '416', ' 133', ' 455', ' 169', '2'], ['11321', '267', '417', ' 133', ' 457', ' 171', '2'], ['11322', '267', '417', ' 133', ' 457', ' 172', '2'], ['11323', '267', '418', ' 133', ' 458', ' 173', '2'], ['11324', '267', '420', ' 134', ' 460', ' 173', '2'], ['11325', '267', '421', ' 135', ' 461', ' 174', '2'], ['11326', '267', '422', ' 136', ' 462', ' 176', '2'], ['11327', '267', '423', ' 136', ' 464', ' 177', '2'], ['11328', '267', '424', ' 138', ' 463', ' 177', '2'], ['11329', '267', '425', ' 139', ' 464', ' 178', '2'], ['11330', '267', '425', ' 139', ' 465', ' 179', '2'], ['11331', '267', '425', ' 140', ' 466', ' 181', '2'], ['11332', '267', '426', ' 141', ' 467', ' 182', '2'], ['11333', '267', '427', ' 142', ' 468', ' 184', '2'], ['11334', '267', '427', ' 143', ' 469', ' 185', '2'], ['11335', '267', '428', ' 143', ' 471', ' 186', '2'], ['11336', '267', '430', ' 144', ' 473', ' 187', '2'], ['11337', '267', '430', ' 145', ' 474', ' 189', '2'], ['11338', '267', '431', ' 146', ' 475', ' 190', '2'], ['11339', '267', '433', ' 147', ' 476', ' 191', '2'], ['11340', '267', '433', ' 149', ' 478', ' 193', '2'], ['11341', '267', '433', ' 150', ' 479', ' 195', '2'], ['11342', '267', '433', ' 150', ' 481', ' 197', '2'], ['11343', '267', '434', ' 151', ' 482', ' 198', '2'], ['11344', '267', '437', ' 152', ' 485', ' 200', '2'], ['11345', '267', '438', ' 153', ' 487', ' 202', '2'], ['11346', '267', '439', ' 155', ' 489', ' 204', '2'], ['11347', '267', '441', ' 156', ' 490', ' 206', '2'], ['11348', '267', '442', ' 157', ' 492', ' 207', '2'], ['11349', '267', '443', ' 158', ' 493', ' 208', '2'], ['11350', '267', '443', ' 159', ' 495', ' 209', '2'], ['11351', '267', '443', ' 159', ' 497', ' 211', '2'], ['11352', '267', '445', ' 160', ' 498', ' 213', '2'], ['11353', '267', '446', ' 162', ' 501', ' 216', '2'], ['11354', '267', '447', ' 163', ' 503', ' 219', '2'], ['11355', '267', '448', ' 164', ' 506', ' 220', '2'], ['11356', '267', '450', ' 166', ' 508', ' 223', '2'], ['11357', '267', '450', ' 167', ' 510', ' 226', '2'], ['11358', '267', '451', ' 167', ' 512', ' 228', '2'], ['11359', '267', '454', ' 168', ' 516', ' 230', '2'], ['11360', '267', '455', ' 169', ' 518', ' 232', '2'], ['11361', '267', '459', ' 173', ' 522', ' 236', '2'], ['11362', '267', '463', ' 176', ' 525', ' 239', '2'], ['11363', '267', '461', ' 176', ' 525', ' 241', '2'], ['11364', '267', '462', ' 177', ' 529', ' 245', '2'], ['11365', '267', '462', ' 178', ' 533', ' 249', '2'], ['11367', '267', '466', ' 182', ' 536', ' 252', '2'], ['11368', '267', '473', ' 190', ' 540', ' 257', '2'], ['11369', '267', '474', ' 191', ' 544', ' 260', '2'], ['11370', '267', '473', ' 188', ' 548', ' 264', '2'], ['11371', '267', '474', ' 190', ' 552', ' 267', '2'], ['11372', '267', '480', ' 195', ' 557', ' 272', '2'], ['11373', '267', '483', ' 202', ' 558', ' 277', '2'], ['11374', '267', '484', ' 203', ' 561', ' 279', '2'], ['11375', '267', '484', ' 200', ' 568', ' 283', '2'], ['11376', '267', '485', ' 201', ' 572', ' 288', '2'], ['11377', '267', '487', ' 202', ' 577', ' 293', '2'], ['11378', '267', '488', ' 204', ' 582', ' 297', '2'], ['11379', '267', '491', ' 206', ' 587', ' 302', '2'], ['11380', '267', '494', ' 209', ' 591', ' 306', '2'], ['11381', '267', '497', ' 213', ' 595', ' 312', '2'], ['11382', '267', '500', ' 217', ' 601', ' 318', '2'], ['11383', '267', '503', ' 219', ' 607', ' 324', '2'], ['11384', '267', '507', ' 222', ' 613', ' 329', '2'], ['11385', '267', '511', ' 224', ' 619', ' 333', '2'], ['11386', '267', '514', ' 228', ' 625', ' 341', '2'], ['11387', '267', '517', ' 231', ' 633', ' 349', '2'], ['11388', '267', '520', ' 235', ' 639', ' 355', '2'], ['11389', '267', '526', ' 240', ' 647', ' 363', '2'], ['11390', '267', '529', ' 243', ' 654', ' 370', '2'], ['11391', '267', '532', ' 247', ' 663', ' 380', '2'], ['11392', '267', '537', ' 252', ' 672', ' 389', '2'], ['11393', '267', '540', ' 256', ' 682', ' 401', '2'], ['11394', '267', '547', ' 262', ' 690', ' 408', '2'], ['11395', '267', '555', ' 267', ' 697', ' 411', '2'], ['11396', '267', '568', ' 273', ' 712', ' 415', '2'], ['11397', '267', '577', ' 277', ' 723', ' 418', '2'], ['11398', '267', '582', ' 280', ' 729', ' 419', '2'], ['11399', '267', '590', ' 288', ' 730', ' 417', '2'], ['11400', '267', '597', ' 296', ' 731', ' 415', '2'], ['11401', '267', '606', ' 303', ' 735', ' 414', '2'], ['11402', '267', '616', ' 310', ' 741', ' 413', '2'], ['11403', '267', '625', ' 318', ' 747', ' 414', '2'], ['11404', '267', '635', ' 326', ' 751', ' 414', '2'], ['11405', '267', '641', ' 329', ' 757', ' 413', '2']], '358': [['13898', '358', '363', ' 109', ' 389', ' 132', '2'], ['13899', '358', '363', ' 109', ' 390', ' 133', '2'], ['13900', '358', '362', ' 109', ' 391', ' 134', '2'], ['13901', '358', '364', ' 111', ' 390', ' 135', '2'], ['13902', '358', '363', ' 109', ' 392', ' 135', '2'], ['13903', '358', '363', ' 109', ' 392', ' 135', '2'], ['13904', '358', '363', ' 109', ' 393', ' 135', '2'], ['13905', '358', '364', ' 109', ' 392', ' 134', '2'], ['13906', '358', '364', ' 109', ' 393', ' 134', '2'], ['13907', '358', '366', ' 113', ' 393', ' 136', '2'], ['13908', '358', '367', ' 115', ' 393', ' 138', '2'], ['13921', '358', '368', ' 115', ' 402', ' 145', '2'], ['13922', '358', '369', ' 114', ' 402', ' 146', '2'], ['13923', '358', '369', ' 114', ' 402', ' 146', '2'], ['13927', '358', '372', ' 118', ' 405', ' 150', '2'], ['13928', '358', '372', ' 118', ' 405', ' 151', '2'], ['13929', '358', '374', ' 120', ' 406', ' 151', '2'], ['13930', '358', '373', ' 122', ' 405', ' 152', '2'], ['13931', '358', '374', ' 124', ' 405', ' 153', '2'], ['13932', '358', '375', ' 125', ' 405', ' 153', '2'], ['13933', '358', '375', ' 125', ' 406', ' 153', '2'], ['13934', '358', '376', ' 127', ' 406', ' 154', '2'], ['13935', '358', '376', ' 126', ' 407', ' 155', '2'], ['13936', '358', '376', ' 126', ' 409', ' 156', '2'], ['13937', '358', '377', ' 127', ' 410', ' 157', '2'], ['13938', '358', '376', ' 127', ' 410', ' 158', '2'], ['13939', '358', '377', ' 129', ' 410', ' 159', '2'], ['13940', '358', '376', ' 129', ' 411', ' 160', '2'], ['13943', '358', '377', ' 129', ' 414', ' 163', '2'], ['13944', '358', '378', ' 130', ' 415', ' 165', '2'], ['13945', '358', '378', ' 131', ' 416', ' 167', '2'], ['13946', '358', '379', ' 131', ' 418', ' 168', '2'], ['13947', '358', '380', ' 132', ' 418', ' 169', '2'], ['13949', '358', '380', ' 133', ' 420', ' 172', '2'], ['13950', '358', '382', ' 135', ' 420', ' 173', '2'], ['13951', '358', '383', ' 137', ' 422', ' 175', '2'], ['13952', '358', '384', ' 139', ' 422', ' 176', '2'], ['13953', '358', '384', ' 138', ' 424', ' 177', '2'], ['13954', '358', '385', ' 140', ' 424', ' 178', '2'], ['13955', '358', '386', ' 141', ' 424', ' 179', '2'], ['13956', '358', '385', ' 139', ' 427', ' 181', '2'], ['13957', '358', '386', ' 141', ' 427', ' 182', '2'], ['13958', '358', '387', ' 143', ' 428', ' 183', '2'], ['13959', '358', '387', ' 142', ' 429', ' 185', '2'], ['13960', '358', '388', ' 144', ' 430', ' 186', '2'], ['13961', '358', '389', ' 146', ' 431', ' 188', '2'], ['13962', '358', '390', ' 146', ' 432', ' 189', '2'], ['13963', '358', '391', ' 147', ' 433', ' 190', '2'], ['13964', '358', '393', ' 148', ' 435', ' 191', '2'], ['13965', '358', '392', ' 149', ' 436', ' 194', '2'], ['13966', '358', '393', ' 149', ' 438', ' 196', '2'], ['13967', '358', '393', ' 149', ' 440', ' 199', '2'], ['13968', '358', '394', ' 152', ' 441', ' 201', '2'], ['13969', '358', '395', ' 152', ' 443', ' 202', '2'], ['13970', '358', '396', ' 153', ' 443', ' 204', '2'], ['13971', '358', '397', ' 157', ' 444', ' 206', '2'], ['13972', '358', '397', ' 154', ' 448', ' 208', '2'], ['13973', '358', '399', ' 157', ' 449', ' 210', '2'], ['13974', '358', '400', ' 158', ' 451', ' 213', '2'], ['13975', '358', '401', ' 161', ' 452', ' 216', '2'], ['13976', '358', '401', ' 161', ' 454', ' 218', '2'], ['13977', '358', '402', ' 163', ' 456', ' 220', '2'], ['13978', '358', '403', ' 165', ' 458', ' 223', '2'], ['13979', '358', '403', ' 166', ' 460', ' 226', '2'], ['13980', '358', '403', ' 166', ' 462', ' 228', '2'], ['13981', '358', '407', ' 169', ' 465', ' 230', '2'], ['13982', '358', '408', ' 169', ' 469', ' 233', '2'], ['13983', '358', '408', ' 170', ' 471', ' 236', '2'], ['13984', '358', '409', ' 172', ' 474', ' 239', '2'], ['13985', '358', '410', ' 173', ' 476', ' 243', '2'], ['13986', '358', '411', ' 174', ' 480', ' 247', '2'], ['13987', '358', '412', ' 177', ' 483', ' 251', '2'], ['13988', '358', '414', ' 179', ' 486', ' 254', '2'], ['13989', '358', '417', ' 182', ' 489', ' 258', '2'], ['13990', '358', '418', ' 184', ' 492', ' 262', '2'], ['13991', '358', '419', ' 185', ' 495', ' 265', '2'], ['13992', '358', '421', ' 188', ' 499', ' 270', '2'], ['13993', '358', '422', ' 190', ' 502', ' 273', '2'], ['13994', '358', '424', ' 193', ' 505', ' 278', '2'], ['13995', '358', '425', ' 195', ' 511', ' 284', '2'], ['13996', '358', '428', ' 197', ' 515', ' 289', '2'], ['13997', '358', '430', ' 200', ' 520', ' 294', '2'], ['13998', '358', '432', ' 202', ' 524', ' 300', '2'], ['13999', '358', '434', ' 206', ' 528', ' 304', '2'], ['14000', '358', '437', ' 210', ' 532', ' 311', '2'], ['14001', '358', '440', ' 214', ' 537', ' 316', '2'], ['14002', '358', '442', ' 217', ' 543', ' 323', '2'], ['14003', '358', '445', ' 220', ' 550', ' 330', '2'], ['14006', '358', '453', ' 231', ' 565', ' 349', '2'], ['14007', '358', '457', ' 236', ' 574', ' 359', '2'], ['14008', '358', '461', ' 242', ' 583', ' 370', '2'], ['14009', '358', '464', ' 245', ' 590', ' 378', '2'], ['14010', '358', '469', ' 250', ' 598', ' 387', '2'], ['14012', '358', '477', ' 261', ' 615', ' 408', '2'], ['14013', '358', '483', ' 267', ' 622', ' 413', '2'], ['14014', '358', '492', ' 272', ' 630', ' 415', '2'], ['14015', '358', '504', ' 278', ' 642', ' 418', '2'], ['14016', '358', '508', ' 285', ' 638', ' 415', '2'], ['14017', '358', '517', ' 293', ' 641', ' 413', '2'], ['14018', '358', '526', ' 301', ' 646', ' 413', '2'], ['14019', '358', '534', ' 309', ' 651', ' 414', '2'], ['14020', '358', '541', ' 317', ' 655', ' 413', '2'], ['14021', '358', '553', ' 322', ' 665', ' 413', '2'], ['14022', '358', '565', ' 335', ' 667', ' 413', '2']], '360': [['13953', '360', '381', ' 107', ' 409', ' 129', '2'], ['13954', '360', '381', ' 107', ' 408', ' 129', '2'], ['13955', '360', '381', ' 107', ' 408', ' 129', '2'], ['13956', '360', '381', ' 108', ' 408', ' 130', '2'], ['13957', '360', '381', ' 108', ' 409', ' 130', '2'], ['13958', '360', '381', ' 108', ' 409', ' 131', '2'], ['13959', '360', '381', ' 108', ' 409', ' 131', '2'], ['13960', '360', '381', ' 107', ' 409', ' 131', '2'], ['13961', '360', '381', ' 107', ' 410', ' 131', '2'], ['13962', '360', '382', ' 107', ' 410', ' 131', '2'], ['13963', '360', '381', ' 107', ' 410', ' 132', '2'], ['13964', '360', '382', ' 108', ' 410', ' 132', '2'], ['13965', '360', '382', ' 108', ' 411', ' 133', '2'], ['13966', '360', '383', ' 109', ' 411', ' 133', '2'], ['13970', '360', '384', ' 109', ' 413', ' 134', '2'], ['13971', '360', '386', ' 111', ' 412', ' 135', '2'], ['13975', '360', '388', ' 113', ' 414', ' 137', '2'], ['13976', '360', '389', ' 115', ' 414', ' 137', '2'], ['13977', '360', '390', ' 117', ' 414', ' 137', '2'], ['13978', '360', '389', ' 117', ' 414', ' 138', '2'], ['13979', '360', '388', ' 116', ' 414', ' 139', '2'], ['13980', '360', '388', ' 117', ' 414', ' 139', '2'], ['13981', '360', '390', ' 117', ' 415', ' 139', '2'], ['13982', '360', '389', ' 116', ' 417', ' 140', '2'], ['13983', '360', '390', ' 117', ' 417', ' 140', '2'], ['13984', '360', '392', ' 119', ' 417', ' 140', '2'], ['13985', '360', '393', ' 120', ' 418', ' 141', '2'], ['13986', '360', '392', ' 120', ' 418', ' 141', '2'], ['13987', '360', '391', ' 118', ' 419', ' 141', '2'], ['13988', '360', '391', ' 117', ' 419', ' 140', '2'], ['13989', '360', '391', ' 116', ' 421', ' 141', '2'], ['13990', '360', '391', ' 115', ' 422', ' 141', '2'], ['13991', '360', '390', ' 114', ' 422', ' 142', '2'], ['13992', '360', '391', ' 114', ' 423', ' 142', '2'], ['13993', '360', '393', ' 116', ' 423', ' 142', '2'], ['13994', '360', '393', ' 118', ' 422', ' 143', '2'], ['14003', '360', '400', ' 126', ' 424', ' 147', '2'], ['14004', '360', '399', ' 126', ' 426', ' 148', '2'], ['14006', '360', '399', ' 126', ' 427', ' 148', '2'], ['14007', '360', '398', ' 124', ' 430', ' 149', '2'], ['14008', '360', '398', ' 124', ' 432', ' 150', '2'], ['14009', '360', '398', ' 125', ' 432', ' 152', '2'], ['14010', '360', '399', ' 126', ' 433', ' 152', '2'], ['14011', '360', '400', ' 126', ' 433', ' 152', '2'], ['14012', '360', '401', ' 127', ' 433', ' 152', '2'], ['14013', '360', '402', ' 128', ' 434', ' 153', '2'], ['14014', '360', '402', ' 128', ' 435', ' 153', '2'], ['14015', '360', '401', ' 128', ' 435', ' 154', '2'], ['14016', '360', '403', ' 130', ' 435', ' 154', '2'], ['14017', '360', '403', ' 131', ' 435', ' 155', '2'], ['14019', '360', '402', ' 129', ' 438', ' 156', '2'], ['14020', '360', '402', ' 129', ' 438', ' 156', '2'], ['14021', '360', '402', ' 127', ' 439', ' 156', '2'], ['14022', '360', '401', ' 126', ' 441', ' 157', '2'], ['14023', '360', '401', ' 125', ' 441', ' 158', '2'], ['14024', '360', '402', ' 126', ' 441', ' 158', '2'], ['14025', '360', '402', ' 126', ' 442', ' 159', '2'], ['14026', '360', '403', ' 127', ' 442', ' 160', '2'], ['14027', '360', '404', ' 129', ' 441', ' 161', '2'], ['14028', '360', '406', ' 132', ' 441', ' 162', '2'], ['14029', '360', '406', ' 129', ' 444', ' 163', '2'], ['14030', '360', '406', ' 130', ' 446', ' 164', '2'], ['14031', '360', '407', ' 129', ' 447', ' 165', '2'], ['14032', '360', '408', ' 130', ' 448', ' 165', '2'], ['14033', '360', '408', ' 131', ' 448', ' 166', '2'], ['14034', '360', '408', ' 132', ' 449', ' 167', '2'], ['14035', '360', '409', ' 133', ' 449', ' 168', '2'], ['14036', '360', '412', ' 136', ' 450', ' 168', '2'], ['14037', '360', '412', ' 137', ' 450', ' 169', '2'], ['14038', '360', '412', ' 138', ' 449', ' 170', '2'], ['14039', '360', '412', ' 138', ' 451', ' 171', '2'], ['14040', '360', '413', ' 139', ' 452', ' 171', '2'], ['14041', '360', '413', ' 139', ' 453', ' 173', '2'], ['14042', '360', '413', ' 139', ' 454', ' 174', '2'], ['14043', '360', '414', ' 141', ' 454', ' 175', '2'], ['14044', '360', '415', ' 141', ' 456', ' 176', '2'], ['14045', '360', '417', ' 143', ' 457', ' 177', '2'], ['14046', '360', '417', ' 144', ' 458', ' 178', '2'], ['14047', '360', '417', ' 144', ' 459', ' 179', '2'], ['14048', '360', '419', ' 144', ' 460', ' 180', '2'], ['14049', '360', '418', ' 145', ' 461', ' 181', '2'], ['14050', '360', '419', ' 145', ' 462', ' 182', '2'], ['14051', '360', '420', ' 146', ' 463', ' 183', '2'], ['14052', '360', '420', ' 146', ' 465', ' 184', '2'], ['14053', '360', '421', ' 146', ' 466', ' 185', '2'], ['14054', '360', '422', ' 147', ' 467', ' 187', '2'], ['14055', '360', '422', ' 147', ' 468', ' 188', '2'], ['14056', '360', '422', ' 146', ' 470', ' 189', '2'], ['14057', '360', '424', ' 149', ' 470', ' 190', '2'], ['14058', '360', '425', ' 150', ' 472', ' 191', '2'], ['14059', '360', '427', ' 151', ' 474', ' 192', '2'], ['14060', '360', '427', ' 151', ' 475', ' 194', '2'], ['14061', '360', '428', ' 153', ' 475', ' 195', '2'], ['14062', '360', '429', ' 153', ' 477', ' 197', '2'], ['14063', '360', '429', ' 154', ' 479', ' 199', '2'], ['14064', '360', '431', ' 155', ' 481', ' 200', '2'], ['14065', '360', '431', ' 155', ' 482', ' 202', '2'], ['14066', '360', '432', ' 156', ' 483', ' 204', '2'], ['14067', '360', '434', ' 158', ' 485', ' 205', '2'], ['14068', '360', '436', ' 159', ' 486', ' 206', '2'], ['14069', '360', '438', ' 161', ' 487', ' 207', '2'], ['14070', '360', '439', ' 162', ' 488', ' 208', '2'], ['14071', '360', '440', ' 163', ' 491', ' 210', '2'], ['14072', '360', '440', ' 163', ' 493', ' 211', '2'], ['14073', '360', '440', ' 164', ' 494', ' 213', '2'], ['14074', '360', '440', ' 165', ' 496', ' 215', '2'], ['14075', '360', '440', ' 165', ' 498', ' 219', '2'], ['14076', '360', '441', ' 165', ' 500', ' 220', '2'], ['14077', '360', '442', ' 168', ' 501', ' 222', '2'], ['14078', '360', '444', ' 169', ' 504', ' 225', '2'], ['14079', '360', '445', ' 170', ' 507', ' 227', '2'], ['14080', '360', '448', ' 171', ' 509', ' 228', '2'], ['14081', '360', '451', ' 176', ' 510', ' 229', '2'], ['14082', '360', '451', ' 175', ' 512', ' 231', '2'], ['14083', '360', '453', ' 176', ' 516', ' 235', '2'], ['14084', '360', '454', ' 178', ' 518', ' 237', '2'], ['14085', '360', '454', ' 179', ' 521', ' 239', '2'], ['14086', '360', '457', ' 182', ' 522', ' 242', '2'], ['14087', '360', '458', ' 185', ' 524', ' 246', '2'], ['14088', '360', '459', ' 186', ' 527', ' 248', '2'], ['14089', '360', '463', ' 189', ' 530', ' 251', '2'], ['14090', '360', '464', ' 190', ' 533', ' 253', '2'], ['14091', '360', '468', ' 193', ' 534', ' 254', '2'], ['14092', '360', '469', ' 195', ' 537', ' 257', '2'], ['14093', '360', '470', ' 197', ' 542', ' 262', '2'], ['14094', '360', '472', ' 199', ' 543', ' 264', '2'], ['14095', '360', '472', ' 200', ' 548', ' 268', '2'], ['14096', '360', '472', ' 200', ' 552', ' 271', '2'], ['14097', '360', '477', ' 206', ' 554', ' 274', '2'], ['14098', '360', '477', ' 205', ' 559', ' 277', '2'], ['14099', '360', '478', ' 204', ' 563', ' 279', '2'], ['14100', '360', '486', ' 213', ' 566', ' 284', '2'], ['14101', '360', '482', ' 207', ' 572', ' 288', '2'], ['14102', '360', '483', ' 208', ' 578', ' 293', '2'], ['14103', '360', '485', ' 209', ' 582', ' 297', '2'], ['14104', '360', '488', ' 212', ' 585', ' 299', '2'], ['14105', '360', '491', ' 216', ' 589', ' 305', '2'], ['14106', '360', '494', ' 218', ' 594', ' 308', '2'], ['14107', '360', '496', ' 220', ' 599', ' 313', '2'], ['14108', '360', '498', ' 222', ' 605', ' 319', '2'], ['14109', '360', '501', ' 224', ' 610', ' 323', '2'], ['14110', '360', '504', ' 226', ' 616', ' 329', '2'], ['14111', '360', '508', ' 231', ' 620', ' 334', '2'], ['14112', '360', '511', ' 234', ' 628', ' 341', '2'], ['14113', '360', '515', ' 238', ' 633', ' 347', '2'], ['14114', '360', '518', ' 241', ' 639', ' 353', '2'], ['14115', '360', '522', ' 245', ' 646', ' 360', '2'], ['14116', '360', '526', ' 251', ' 652', ' 367', '2'], ['14117', '360', '530', ' 252', ' 661', ' 375', '2'], ['14118', '360', '535', ' 256', ' 669', ' 382', '2'], ['14119', '360', '537', ' 261', ' 678', ' 393', '2'], ['14120', '360', '541', ' 265', ' 686', ' 402', '2'], ['14121', '360', '547', ' 269', ' 693', ' 407', '2'], ['14122', '360', '553', ' 273', ' 700', ' 412', '2'], ['14123', '360', '562', ' 278', ' 709', ' 414', '2'], ['14124', '360', '574', ' 282', ' 721', ' 416', '2'], ['14125', '360', '582', ' 288', ' 726', ' 417', '2'], ['14126', '360', '589', ' 295', ' 728', ' 416', '2'], ['14127', '360', '595', ' 301', ' 732', ' 417', '2'], ['14128', '360', '604', ' 308', ' 732', ' 414', '2'], ['14129', '360', '613', ' 315', ' 738', ' 413', '2'], ['14130', '360', '621', ' 320', ' 745', ' 414', '2'], ['14131', '360', '628', ' 323', ' 751', ' 413', '2'], ['14132', '360', '638', ' 333', ' 752', ' 413', '2'], ['14133', '360', '646', ' 343', ' 751', ' 413', '2'], ['14135', '360', '666', ' 360', ' 753', ' 414', '2']], '389': [['14464', '389', '366', ' 105', ' 389', ' 119', '2'], ['14465', '389', '366', ' 104', ' 390', ' 119', '2'], ['14466', '389', '366', ' 104', ' 390', ' 119', '2'], ['14467', '389', '367', ' 104', ' 390', ' 119', '2'], ['14468', '389', '368', ' 105', ' 390', ' 119', '2'], ['14469', '389', '368', ' 106', ' 390', ' 119', '2'], ['14470', '389', '368', ' 105', ' 390', ' 119', '2'], ['14471', '389', '368', ' 105', ' 390', ' 118', '2'], ['14472', '389', '368', ' 105', ' 390', ' 118', '2'], ['14473', '389', '368', ' 106', ' 390', ' 119', '2'], ['14477', '389', '369', ' 106', ' 389', ' 118', '2'], ['14478', '389', '368', ' 107', ' 390', ' 119', '2'], ['14479', '389', '369', ' 107', ' 390', ' 119', '2'], ['14483', '389', '369', ' 106', ' 391', ' 119', '2'], ['14484', '389', '369', ' 106', ' 391', ' 119', '2'], ['14485', '389', '370', ' 107', ' 392', ' 120', '2'], ['14486', '389', '370', ' 107', ' 392', ' 120', '2'], ['14487', '389', '370', ' 107', ' 393', ' 120', '2'], ['14488', '389', '369', ' 107', ' 394', ' 121', '2'], ['14489', '389', '369', ' 107', ' 393', ' 121', '2'], ['14490', '389', '369', ' 106', ' 393', ' 121', '2'], ['14496', '389', '368', ' 106', ' 394', ' 121', '2'], ['14497', '389', '369', ' 106', ' 394', ' 121', '2'], ['14498', '389', '370', ' 106', ' 393', ' 121', '2'], ['14499', '389', '370', ' 106', ' 393', ' 120', '2'], ['14500', '389', '370', ' 106', ' 393', ' 120', '2'], ['14501', '389', '370', ' 106', ' 393', ' 120', '2'], ['14502', '389', '370', ' 106', ' 394', ' 121', '2'], ['14513', '389', '370', ' 107', ' 395', ' 122', '2'], ['14514', '389', '370', ' 107', ' 396', ' 122', '2'], ['14515', '389', '369', ' 107', ' 397', ' 123', '2'], ['14516', '389', '369', ' 107', ' 397', ' 123', '2'], ['14517', '389', '369', ' 106', ' 397', ' 124', '2'], ['14518', '389', '369', ' 106', ' 398', ' 124', '2'], ['14519', '389', '369', ' 105', ' 398', ' 124', '2'], ['14520', '389', '368', ' 104', ' 399', ' 124', '2'], ['14521', '389', '368', ' 104', ' 400', ' 125', '2'], ['14522', '389', '370', ' 105', ' 400', ' 125', '2'], ['14523', '389', '371', ' 105', ' 400', ' 125', '2'], ['14524', '389', '371', ' 105', ' 400', ' 125', '2'], ['14525', '389', '372', ' 107', ' 399', ' 125', '2'], ['14526', '389', '373', ' 108', ' 398', ' 125', '2'], ['14527', '389', '373', ' 109', ' 398', ' 126', '2'], ['14528', '389', '373', ' 109', ' 398', ' 126', '2'], ['14529', '389', '373', ' 109', ' 398', ' 126', '2'], ['14530', '389', '374', ' 109', ' 398', ' 126', '2'], ['14531', '389', '374', ' 110', ' 398', ' 126', '2'], ['14532', '389', '375', ' 110', ' 398', ' 126', '2'], ['14533', '389', '375', ' 110', ' 398', ' 126', '2'], ['14534', '389', '375', ' 111', ' 398', ' 126', '2'], ['14535', '389', '374', ' 110', ' 399', ' 126', '2'], ['14536', '389', '374', ' 110', ' 399', ' 127', '2'], ['14537', '389', '374', ' 110', ' 399', ' 126', '2'], ['14538', '389', '374', ' 110', ' 399', ' 127', '2'], ['14539', '389', '374', ' 110', ' 398', ' 127', '2'], ['14546', '389', '376', ' 114', ' 400', ' 130', '2'], ['14547', '389', '376', ' 114', ' 402', ' 131', '2'], ['14548', '389', '375', ' 113', ' 403', ' 132', '2'], ['14549', '389', '375', ' 112', ' 403', ' 132', '2'], ['14550', '389', '375', ' 112', ' 403', ' 132', '2'], ['14551', '389', '375', ' 113', ' 402', ' 132', '2'], ['14553', '389', '375', ' 113', ' 403', ' 133', '2'], ['14554', '389', '375', ' 113', ' 403', ' 133', '2'], ['14555', '389', '375', ' 113', ' 403', ' 133', '2'], ['14557', '389', '375', ' 112', ' 405', ' 133', '2'], ['14558', '389', '375', ' 112', ' 405', ' 134', '2'], ['14559', '389', '376', ' 113', ' 405', ' 134', '2'], ['14560', '389', '377', ' 113', ' 405', ' 134', '2'], ['14561', '389', '376', ' 113', ' 405', ' 134', '2'], ['14562', '389', '377', ' 114', ' 405', ' 134', '2'], ['14563', '389', '377', ' 114', ' 405', ' 134', '2'], ['14564', '389', '377', ' 114', ' 405', ' 134', '2'], ['14565', '389', '376', ' 113', ' 406', ' 134', '2'], ['14566', '389', '377', ' 113', ' 407', ' 135', '2'], ['14567', '389', '378', ' 113', ' 408', ' 135', '2'], ['14568', '389', '378', ' 113', ' 409', ' 135', '2'], ['14569', '389', '378', ' 113', ' 409', ' 135', '2'], ['14570', '389', '378', ' 113', ' 409', ' 136', '2'], ['14571', '389', '378', ' 113', ' 409', ' 136', '2'], ['14572', '389', '378', ' 113', ' 410', ' 137', '2'], ['14573', '389', '378', ' 113', ' 410', ' 137', '2'], ['14574', '389', '377', ' 111', ' 411', ' 137', '2'], ['14575', '389', '377', ' 111', ' 412', ' 137', '2'], ['14576', '389', '377', ' 111', ' 412', ' 137', '2'], ['14577', '389', '377', ' 110', ' 413', ' 138', '2'], ['14578', '389', '377', ' 109', ' 413', ' 138', '2'], ['14579', '389', '378', ' 109', ' 413', ' 138', '2'], ['14580', '389', '379', ' 111', ' 413', ' 138', '2'], ['14581', '389', '380', ' 111', ' 414', ' 139', '2'], ['14582', '389', '381', ' 111', ' 414', ' 139', '2'], ['14583', '389', '381', ' 111', ' 414', ' 139', '2'], ['14584', '389', '381', ' 111', ' 414', ' 139', '2'], ['14585', '389', '381', ' 111', ' 414', ' 139', '2'], ['14586', '389', '382', ' 111', ' 414', ' 139', '2'], ['14587', '389', '382', ' 111', ' 415', ' 139', '2'], ['14588', '389', '382', ' 112', ' 414', ' 139', '2'], ['14589', '389', '383', ' 112', ' 415', ' 139', '2'], ['14599', '389', '385', ' 117', ' 416', ' 143', '2'], ['14600', '389', '386', ' 118', ' 417', ' 144', '2'], ['14601', '389', '387', ' 119', ' 417', ' 144', '2'], ['14604', '389', '389', ' 122', ' 416', ' 145', '2'], ['14607', '389', '389', ' 122', ' 417', ' 145', '2'], ['14608', '389', '389', ' 122', ' 418', ' 145', '2'], ['14609', '389', '389', ' 121', ' 419', ' 145', '2'], ['14610', '389', '389', ' 121', ' 419', ' 146', '2'], ['14611', '389', '389', ' 121', ' 420', ' 146', '2'], ['14612', '389', '390', ' 121', ' 420', ' 147', '2'], ['14613', '389', '390', ' 121', ' 420', ' 147', '2'], ['14614', '389', '390', ' 122', ' 420', ' 147', '2'], ['14615', '389', '390', ' 122', ' 420', ' 148', '2'], ['14616', '389', '390', ' 123', ' 421', ' 148', '2'], ['14617', '389', '391', ' 123', ' 422', ' 149', '2'], ['14618', '389', '391', ' 125', ' 422', ' 149', '2'], ['14619', '389', '392', ' 125', ' 422', ' 150', '2'], ['14620', '389', '392', ' 124', ' 424', ' 150', '2'], ['14621', '389', '391', ' 124', ' 425', ' 151', '2'], ['14622', '389', '391', ' 124', ' 425', ' 151', '2'], ['14623', '389', '391', ' 126', ' 424', ' 152', '2'], ['14624', '389', '392', ' 126', ' 425', ' 152', '2'], ['14625', '389', '392', ' 126', ' 425', ' 152', '2'], ['14626', '389', '392', ' 127', ' 425', ' 152', '2'], ['14627', '389', '393', ' 127', ' 426', ' 152', '2'], ['14628', '389', '393', ' 126', ' 427', ' 153', '2'], ['14629', '389', '393', ' 126', ' 428', ' 153', '2'], ['14630', '389', '393', ' 126', ' 429', ' 154', '2'], ['14631', '389', '393', ' 126', ' 429', ' 155', '2'], ['14632', '389', '393', ' 126', ' 429', ' 155', '2'], ['14633', '389', '394', ' 127', ' 430', ' 156', '2'], ['14634', '389', '395', ' 127', ' 431', ' 156', '2'], ['14635', '389', '396', ' 128', ' 432', ' 157', '2'], ['14636', '389', '395', ' 128', ' 432', ' 157', '2'], ['14637', '389', '396', ' 129', ' 432', ' 158', '2'], ['14638', '389', '396', ' 129', ' 432', ' 158', '2'], ['14639', '389', '396', ' 129', ' 433', ' 158', '2'], ['14640', '389', '397', ' 129', ' 434', ' 159', '2'], ['14641', '389', '397', ' 129', ' 434', ' 159', '2'], ['14642', '389', '398', ' 131', ' 433', ' 159', '2'], ['14643', '389', '399', ' 131', ' 434', ' 160', '2'], ['14644', '389', '398', ' 131', ' 434', ' 160', '2'], ['14645', '389', '399', ' 131', ' 435', ' 161', '2'], ['14646', '389', '399', ' 132', ' 435', ' 161', '2'], ['14647', '389', '400', ' 133', ' 437', ' 163', '2'], ['14648', '389', '400', ' 133', ' 438', ' 164', '2'], ['14649', '389', '399', ' 133', ' 438', ' 164', '2'], ['14650', '389', '399', ' 133', ' 438', ' 165', '2'], ['14651', '389', '399', ' 134', ' 438', ' 165', '2'], ['14652', '389', '400', ' 134', ' 440', ' 166', '2'], ['14653', '389', '400', ' 134', ' 441', ' 166', '2'], ['14654', '389', '400', ' 134', ' 441', ' 167', '2'], ['14655', '389', '401', ' 135', ' 441', ' 168', '2'], ['14656', '389', '400', ' 135', ' 443', ' 169', '2'], ['14657', '389', '400', ' 135', ' 443', ' 170', '2'], ['14658', '389', '401', ' 135', ' 443', ' 170', '2'], ['14659', '389', '403', ' 137', ' 444', ' 171', '2'], ['14660', '389', '403', ' 138', ' 444', ' 171', '2'], ['14661', '389', '403', ' 138', ' 444', ' 171', '2'], ['14662', '389', '403', ' 138', ' 444', ' 172', '2'], ['14663', '389', '404', ' 139', ' 444', ' 172', '2'], ['14664', '389', '405', ' 141', ' 445', ' 173', '2'], ['14665', '389', '406', ' 141', ' 446', ' 173', '2'], ['14666', '389', '406', ' 141', ' 447', ' 174', '2'], ['14667', '389', '405', ' 140', ' 449', ' 175', '2'], ['14668', '389', '405', ' 140', ' 450', ' 176', '2'], ['14669', '389', '406', ' 140', ' 450', ' 177', '2'], ['14670', '389', '407', ' 141', ' 450', ' 177', '2'], ['14671', '389', '407', ' 142', ' 450', ' 177', '2'], ['14672', '389', '407', ' 142', ' 451', ' 178', '2'], ['14673', '389', '407', ' 142', ' 452', ' 179', '2'], ['14674', '389', '408', ' 142', ' 455', ' 181', '2'], ['14675', '389', '408', ' 143', ' 454', ' 181', '2'], ['14676', '389', '408', ' 143', ' 453', ' 181', '2'], ['14677', '389', '410', ' 146', ' 454', ' 184', '2'], ['14678', '389', '409', ' 146', ' 455', ' 185', '2'], ['14679', '389', '409', ' 146', ' 456', ' 186', '2'], ['14680', '389', '410', ' 146', ' 456', ' 186', '2'], ['14681', '389', '411', ' 148', ' 456', ' 187', '2'], ['14682', '389', '411', ' 148', ' 457', ' 187', '2'], ['14683', '389', '412', ' 149', ' 457', ' 188', '2'], ['14684', '389', '413', ' 149', ' 458', ' 188', '2'], ['14685', '389', '412', ' 149', ' 459', ' 189', '2'], ['14686', '389', '413', ' 149', ' 461', ' 190', '2'], ['14687', '389', '413', ' 149', ' 462', ' 191', '2'], ['14688', '389', '413', ' 148', ' 462', ' 192', '2'], ['14689', '389', '413', ' 148', ' 463', ' 193', '2'], ['14690', '389', '414', ' 149', ' 463', ' 193', '2'], ['14691', '389', '415', ' 150', ' 464', ' 194', '2'], ['14692', '389', '414', ' 150', ' 466', ' 197', '2'], ['14693', '389', '414', ' 150', ' 466', ' 198', '2'], ['14694', '389', '414', ' 151', ' 467', ' 199', '2'], ['14695', '389', '415', ' 152', ' 466', ' 200', '2'], ['14696', '389', '416', ' 153', ' 467', ' 201', '2'], ['14697', '389', '417', ' 154', ' 468', ' 202', '2'], ['14698', '389', '417', ' 155', ' 468', ' 203', '2'], ['14699', '389', '419', ' 156', ' 469', ' 203', '2'], ['14700', '389', '418', ' 157', ' 469', ' 205', '2'], ['14701', '389', '419', ' 158', ' 471', ' 206', '2'], ['14702', '389', '420', ' 158', ' 471', ' 207', '2'], ['14703', '389', '420', ' 159', ' 472', ' 208', '2'], ['14704', '389', '420', ' 160', ' 473', ' 210', '2'], ['14705', '389', '421', ' 161', ' 474', ' 211', '2'], ['14706', '389', '422', ' 161', ' 474', ' 210', '2'], ['14707', '389', '422', ' 162', ' 474', ' 211', '2'], ['14708', '389', '422', ' 162', ' 477', ' 213', '2'], ['14709', '389', '423', ' 162', ' 479', ' 216', '2'], ['14710', '389', '424', ' 164', ' 480', ' 218', '2'], ['14711', '389', '424', ' 164', ' 482', ' 220', '2'], ['14712', '389', '425', ' 165', ' 483', ' 221', '2'], ['14713', '389', '425', ' 167', ' 484', ' 223', '2'], ['14714', '389', '427', ' 168', ' 484', ' 223', '2'], ['14715', '389', '427', ' 168', ' 484', ' 223', '2'], ['14716', '389', '427', ' 168', ' 485', ' 224', '2'], ['14717', '389', '427', ' 169', ' 486', ' 226', '2'], ['14718', '389', '428', ' 170', ' 488', ' 228', '2'], ['14719', '389', '429', ' 171', ' 491', ' 230', '2'], ['14720', '389', '429', ' 171', ' 493', ' 232', '2'], ['14721', '389', '430', ' 172', ' 495', ' 233', '2'], ['14722', '389', '430', ' 172', ' 496', ' 235', '2'], ['14723', '389', '430', ' 173', ' 497', ' 236', '2'], ['14724', '389', '432', ' 175', ' 497', ' 237', '2'], ['14725', '389', '431', ' 175', ' 500', ' 239', '2'], ['14726', '389', '431', ' 175', ' 502', ' 242', '2'], ['14727', '389', '433', ' 176', ' 504', ' 243', '2'], ['14728', '389', '434', ' 178', ' 506', ' 247', '2'], ['14729', '389', '436', ' 182', ' 508', ' 249', '2'], ['14730', '389', '437', ' 183', ' 508', ' 250', '2'], ['14731', '389', '437', ' 186', ' 509', ' 253', '2'], ['14732', '389', '438', ' 187', ' 511', ' 255', '2'], ['14733', '389', '440', ' 190', ' 513', ' 257', '2'], ['14734', '389', '439', ' 190', ' 516', ' 261', '2'], ['14735', '389', '441', ' 190', ' 519', ' 261', '2'], ['14736', '389', '440', ' 189', ' 523', ' 265', '2'], ['14737', '389', '441', ' 191', ' 525', ' 269', '2'], ['14738', '389', '443', ' 192', ' 527', ' 270', '2'], ['14739', '389', '443', ' 193', ' 530', ' 274', '2'], ['14740', '389', '446', ' 194', ' 532', ' 275', '2'], ['14741', '389', '447', ' 196', ' 535', ' 278', '2'], ['14742', '389', '449', ' 199', ' 537', ' 281', '2'], ['14743', '389', '450', ' 200', ' 538', ' 283', '2'], ['14744', '389', '451', ' 202', ' 541', ' 285', '2'], ['14745', '389', '450', ' 203', ' 546', ' 292', '2'], ['14746', '389', '452', ' 206', ' 548', ' 296', '2'], ['14747', '389', '455', ' 208', ' 551', ' 297', '2'], ['14748', '389', '457', ' 211', ' 553', ' 300', '2'], ['14749', '389', '458', ' 214', ' 555', ' 304', '2'], ['14750', '389', '460', ' 216', ' 559', ' 307', '2'], ['14751', '389', '461', ' 217', ' 562', ' 310', '2'], ['14752', '389', '463', ' 219', ' 566', ' 313', '2'], ['14753', '389', '464', ' 220', ' 570', ' 317', '2'], ['14754', '389', '466', ' 223', ' 574', ' 322', '2'], ['14755', '389', '468', ' 224', ' 579', ' 325', '2'], ['14756', '389', '470', ' 226', ' 583', ' 330', '2'], ['14757', '389', '472', ' 228', ' 587', ' 334', '2'], ['14758', '389', '475', ' 231', ' 591', ' 338', '2'], ['14759', '389', '476', ' 235', ' 595', ' 344', '2'], ['14760', '389', '480', ' 238', ' 600', ' 348', '2'], ['14761', '389', '482', ' 241', ' 605', ' 354', '2'], ['14762', '389', '484', ' 243', ' 610', ' 359', '2'], ['14763', '389', '486', ' 245', ' 615', ' 364', '2'], ['14764', '389', '488', ' 247', ' 619', ' 369', '2'], ['14765', '389', '490', ' 251', ' 625', ' 376', '2'], ['14766', '389', '493', ' 254', ' 632', ' 383', '2'], ['14767', '389', '496', ' 257', ' 638', ' 389', '2'], ['14768', '389', '498', ' 260', ' 645', ' 398', '2'], ['14769', '389', '502', ' 264', ' 652', ' 406', '2'], ['14770', '389', '506', ' 267', ' 656', ' 410', '2'], ['14771', '389', '511', ' 271', ' 660', ' 412', '2'], ['14772', '389', '516', ' 275', ' 663', ' 414', '2'], ['14773', '389', '522', ' 279', ' 667', ' 414', '2'], ['14774', '389', '527', ' 282', ' 672', ' 414', '2'], ['14775', '389', '534', ' 287', ' 677', ' 414', '2'], ['14776', '389', '539', ' 291', ' 680', ' 415', '2'], ['14777', '389', '543', ' 295', ' 680', ' 412', '2'], ['14778', '389', '550', ' 301', ' 683', ' 411', '2']]}


{'2': [['82', '2', '366', ' 103', ' 394', ' 125', '2'],
  ['83', '2', '366', ' 102', ' 395', ' 126', '2'],
  ['84', '2', '366', ' 103', ' 395', ' 127', '2'],
  ['85', '2', '367', ' 103', ' 395', ' 127', '2'],
  ['86', '2', '367', ' 104', ' 395', ' 127', '2'],
  ['87', '2', '367', ' 103', ' 396', ' 127', '2'],
  ['88', '2', '367', ' 103', ' 396', ' 127', '2'],
  ['89', '2', '367', ' 103', ' 396', ' 127', '2'],
  ['90', '2', '367', ' 103', ' 397', ' 127', '2'],
  ['91', '2', '367', ' 103', ' 398', ' 128', '2'],
  ['92', '2', '367', ' 103', ' 398', ' 128', '2'],
  ['93', '2', '366', ' 104', ' 398', ' 129', '2'],
  ['94', '2', '366', ' 104', ' 398', ' 130', '2'],
  ['95', '2', '367', ' 104', ' 399', ' 130', '2'],
  ['96', '2', '368', ' 105', ' 399', ' 130', '2'],
  ['97', '2', '368', ' 105', ' 399', ' 131', '2'],
  ['98', '2', '369', ' 106', ' 399', ' 131', '2'],
  ['99', '2', '369', ' 106', ' 400', ' 131', '2'],
  ['100', '2', '369', ' 107', ' 401', ' 132', '2'],
  ['101', '2', '370', ' 1

In [4]:
idx=[2, 5, 41, 56, 59, 78, 77, 89, 98, 99, 105, 113, 117, 129, 134, 130, 144, 150, 157, 180, 186, 248, 261, 274, 367, 369, 403],
voilation_id_tracker={2: 220, 5: 252, 41: 1571, 56: 2463, 59: 2867, 78: 3691, 77: 3740, 89: 3817, 98: 4258, 99: 4336, 105: 4560, 113: 4883, 117: 4928, 129: 5574, 134: 5670, 130: 5688, 144: 6560, 150: 6773, 157: 7818, 180: 8774, 186: 9107, 248: 10537, 261: 10751, 274: 11382, 367: 14001, 369: 14107, 403: 14752},
violation_frame_tracker=['/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/2', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/5', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/41', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/56', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/59', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/78', 
 '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/77', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/89', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/98', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/99', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/105', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/113', 
 '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/117', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/129', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/134', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/130', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/144', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/150', 
 '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/157', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/180', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/186', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/248', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/261', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/274', 
 '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/367', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/369', '/home/hlink/workspace/learning/boxmot/30_05_2024_infenrence_output/evidance_clips/403'],

evidance_clip_dir_paths=[{'2': [['67', '2', '364', ' 101', ' 388', ' 121', '2'], ['68', '2', '365', ' 103', ' 387', ' 120', '2'], ['74', '2', '366', ' 104', ' 390', ' 122', '2'], ['75', '2', '366', ' 104', ' 391', ' 123', '2'], ['76', '2', '366', ' 104', ' 392', ' 124', '2'], ['77', '2', '365', ' 104', ' 392', ' 124', '2'], ['78', '2', '366', ' 104', ' 391', ' 124', '2'], ['79', '2', '365', ' 104', ' 391', ' 124', '2'], ['80', '2', '365', ' 103', ' 393', ' 124', '2'], ['81', '2', '365', ' 103', ' 394', ' 125', '2'], ['82', '2', '365', ' 103', ' 395', ' 126', '2'], 
        ['83', '2', '365', ' 103', ' 396', ' 126', '2'], ['84', '2', '365', ' 103', ' 396', ' 127', '2'], ['85', '2', '365', ' 103', ' 396', ' 127', '2'], ['86', '2', '366', ' 103', ' 396', ' 127', '2'], ['87', '2', '366', ' 103', ' 396', ' 127', '2'], ['88', '2', '366', ' 103', ' 397', ' 127', '2'], ['89', '2', '366', ' 102', ' 397', ' 127', '2'], ['90', '2', '366', ' 102', ' 398', ' 127', '2'], ['91', '2', '366', ' 102', ' 398', ' 128', '2'], ['92', '2', '366', ' 103', ' 398', ' 129', '2'], ['93', '2', '366', ' 103', ' 398', ' 129', '2'], 
        ['94', '2', '366', ' 103', ' 399', ' 130', '2'], ['95', '2', '366', ' 103', ' 399', ' 130', '2'], ['96', '2', '367', ' 105', ' 399', ' 130', '2'], ['97', '2', '368', ' 105', ' 399', ' 131', '2'], ['98', '2', '369', ' 106', ' 399', ' 131', '2'], ['99', '2', '369', ' 106', ' 400', ' 131', '2'], ['100', '2', '369', ' 107', ' 401', ' 132', '2'], ['101', '2', '370', ' 107', ' 402', ' 133', '2'], ['102', '2', '373', ' 111', ' 401', ' 133', '2'], ['103', '2', '374', ' 112', ' 401', ' 134', '2'], ['104', '2', '374', ' 112', ' 401', ' 134', '2'], 
        ['105', '2', '374', ' 111', ' 402', ' 134', '2'], ['106', '2', '372', ' 109', ' 403', ' 134', '2'], ['107', '2', '372', ' 109', ' 403', ' 134', '2'], ['108', '2', '371', ' 109', ' 403', ' 134', '2'], ['112', '2', '370', ' 108', ' 406', ' 137', '2'], ['113', '2', '369', ' 107', ' 407', ' 138', '2'], ['116', '2', '378', ' 115', ' 409', ' 140', '2'], ['117', '2', '380', ' 118', ' 408', ' 141', '2'], ['118', '2', '381', ' 119', ' 408', ' 141', '2'], ['119', '2', '381', ' 118', ' 409', ' 141', '2'], ['120', '2', '379', ' 113', ' 412', ' 140', '2'], 
        ['121', '2', '379', ' 113', ' 412', ' 140', '2'], ['122', '2', '379', ' 114', ' 413', ' 142', '2'], ['124', '2', '379', ' 114', ' 413', ' 143', '2'], ['125', '2', '379', ' 114', ' 414', ' 144', '2'], ['128', '2', '382', ' 117', ' 414', ' 145', '2'], ['131', '2', '387', ' 123', ' 414', ' 146', '2'], ['132', '2', '389', ' 126', ' 414', ' 147', '2'], ['133', '2', '390', ' 128', ' 415', ' 147', '2'], ['134', '2', '390', ' 129', ' 417', ' 150', '2'], ['135', '2', '390', ' 129', ' 419', ' 151', '2'], ['136', '2', '391', ' 129', ' 420', ' 151', '2'], 
        ['137', '2', '391', ' 129', ' 421', ' 152', '2'], ['138', '2', '391', ' 129', ' 423', ' 152', '2'], ['139', '2', '392', ' 130', ' 423', ' 153', '2'], ['140', '2', '392', ' 131', ' 422', ' 153', '2'], ['141', '2', '392', ' 131', ' 424', ' 154', '2'], ['142', '2', '392', ' 131', ' 425', ' 155', '2'], ['143', '2', '391', ' 131', ' 425', ' 155', '2'], ['144', '2', '393', ' 132', ' 425', ' 156', '2'], ['145', '2', '392', ' 132', ' 426', ' 157', '2'], ['146', '2', '393', ' 132', ' 428', ' 157', '2'], ['147', '2', '395', ' 133', ' 428', ' 156', '2'], 
        ['148', '2', '395', ' 133', ' 429', ' 158', '2'], ['149', '2', '397', ' 135', ' 432', ' 160', '2'], ['150', '2', '397', ' 135', ' 434', ' 161', '2'], ['151', '2', '397', ' 134', ' 436', ' 162', '2'], ['152', '2', '396', ' 135', ' 437', ' 164', '2'], ['153', '2', '397', ' 136', ' 438', ' 165', '2'], ['154', '2', '399', ' 137', ' 440', ' 166', '2'], ['155', '2', '401', ' 138', ' 441', ' 167', '2'], ['156', '2', '401', ' 138', ' 442', ' 167', '2'], ['157', '2', '401', ' 139', ' 442', ' 168', '2'], ['158', '2', '401', ' 140', ' 443', ' 169', '2'], ['159', '2', '400', ' 141', ' 443', ' 171', '2'], ['160', '2', '400', ' 141', ' 444', ' 172', '2'], ['161', '2', '401', ' 141', ' 444', ' 173', '2'], ['162', '2', '403', ' 143', ' 444', ' 173', '2'], ['163', '2', '404', ' 144', ' 445', ' 174', '2'], ['164', '2', '405', ' 145', ' 446', ' 174', '2'], ['165', '2', '406', ' 145', ' 448', ' 175', '2'], ['166', '2', '406', ' 146', ' 449', ' 178', '2'], ['167', '2', '407', ' 146', ' 451', ' 179', '2'], ['168', '2', '407', ' 146', ' 452', ' 180', '2'], ['169', '2', '409', ' 147', ' 455', ' 181', '2'], ['170', '2', '409', ' 148', ' 456', ' 183', '2'], ['171', '2', '410', ' 149', ' 456', ' 183', '2'], ['172', '2', '411', ' 148', ' 459', ' 184', '2'], ['173', '2', '413', ' 149', ' 460', ' 185', '2'], ['174', '2', '414', ' 150', ' 461', ' 186', '2'], ['175', '2', '416', ' 150', ' 462', ' 187', '2'], ['176', '2', '417', ' 151', ' 463', ' 188', '2'], ['177', '2', '418', ' 153', ' 464', ' 189', '2'], ['178', '2', '418', ' 154', ' 466', ' 191', '2'], ['179', '2', '420', ' 155', ' 468', ' 193', '2'], ['180', '2', '421', ' 157', ' 469', ' 194', '2'], ['181', '2', '422', ' 158', ' 471', ' 197', '2'], ['182', '2', '423', ' 159', ' 472', ' 198', '2'], ['183', '2', '423', ' 160', ' 475', ' 201', '2'], ['184', '2', '424', ' 161', ' 476', ' 203', '2'], ['185', '2', '425', ' 162', ' 478', ' 204', '2'], ['186', '2', '425', ' 163', ' 479', ' 206', '2'], ['187', '2', '426', ' 164', ' 480', ' 207', '2'], ['188', '2', '427', ' 165', ' 481', ' 208', '2'], ['189', '2', '429', ' 168', ' 482', ' 210', '2'], ['190', '2', '430', ' 168', ' 484', ' 211', '2'], ['191', '2', '431', ' 169', ' 486', ' 213', '2'], ['192', '2', '432', ' 171', ' 487', ' 215', '2'], ['193', '2', '433', ' 172', ' 490', ' 217', '2'], ['194', '2', '435', ' 173', ' 493', ' 219', '2'], ['195', '2', '436', ' 175', ' 495', ' 223', '2'], ['196', '2', '438', ' 177', ' 496', ' 224', '2'], ['197', '2', '439', ' 178', ' 498', ' 226', '2'], ['198', '2', '440', ' 180', ' 501', ' 229', '2'], ['199', '2', '442', ' 182', ' 504', ' 231', '2'], ['200', '2', '442', ' 183', ' 506', ' 235', '2'], ['201', '2', '444', ' 185', ' 508', ' 237', '2'], ['202', '2', '446', ' 186', ' 511', ' 239', '2'], ['203', '2', '446', ' 188', ' 512', ' 242', '2'], ['204', '2', '449', ' 192', ' 514', ' 245', '2'], ['205', '2', '450', ' 193', ' 518', ' 248', '2'], ['206', '2', '452', ' 195', ' 520', ' 250', '2'], ['207', '2', '453', ' 197', ' 524', ' 255', '2'], ['208', '2', '454', ' 199', ' 527', ' 258', '2'], ['209', '2', '456', ' 201', ' 530', ' 261', '2'], ['210', '2', '457', ' 202', ' 532', ' 263', '2'], ['211', '2', '458', ' 203', ' 535', ' 266', '2'], ['212', '2', '458', ' 203', ' 539', ' 271', '2'], ['213', '2', '461', ' 208', ' 541', ' 274', '2'], ['214', '2', '464', ' 212', ' 544', ' 278', '2'], ['215', '2', '466', ' 215', ' 548', ' 283', '2'], ['216', '2', '469', ' 217', ' 552', ' 286', '2'], ['217', '2', '471', ' 219', ' 555', ' 290', '2'], ['218', '2', '472', ' 222', ' 561', ' 296', '2'], ['219', '2', '475', ' 224', ' 563', ' 299', '2'], ['220', '2', '475', ' 227', ' 568', ' 305', '2'], ['221', '2', '478', ' 231', ' 572', ' 310', '2'], ['222', '2', '481', ' 234', ' 576', ' 314', '2'], ['223', '2', '484', ' 237', ' 581', ' 320', '2'], ['224', '2', '488', ' 242', ' 586', ' 324', '2'], ['225', '2', '491', ' 245', ' 592', ' 331', '2'], ['226', '2', '493', ' 248', ' 598', ' 337', '2'], ['227', '2', '496', ' 252', ' 604', ' 344', '2'], ['228', '2', '500', ' 256', ' 610', ' 350', '2'], ['229', '2', '502', ' 261', ' 616', ' 358', '2'], ['230', '2', '506', ' 267', ' 621', ' 364', '2'], ['231', '2', '510', ' 271', ' 629', ' 373', '2'], ['232', '2', '515', ' 276', ' 638', ' 381', '2'], ['233', '2', '518', ' 279', ' 647', ' 389', '2'], ['234', '2', '521', ' 284', ' 655', ' 399', '2'], ['235', '2', '526', ' 291', ' 663', ' 410', '2'], ['236', '2', '533', ' 297', ' 669', ' 415', '2'], ['237', '2', '542', ' 305', ' 673', ' 416', '2'], ['238', '2', '551', ' 311', ' 677', ' 417', '2'], ['239', '2', '559', ' 319', ' 680', ' 417', '2'], ['240', '2', '572', ' 323', ' 692', ' 416', '2'], ['241', '2', '576', ' 330', ' 690', ' 416', '2'], ['242', '2', '590', ' 340', ' 696', ' 415', '2'], ['243', '2', '601', ' 350', ' 700', ' 415', '2'], ['244', '2', '611', ' 360', ' 701', ' 415', '2']]}, {'5': [['136', '5', '368', ' 108', ' 397', ' 129', '2'], ['137', '5', '367', ' 108', ' 397', ' 130', '2'], ['140', '5', '369', ' 109', ' 400', ' 131', '2'], ['141', '5', '370', ' 109', ' 401', ' 131', '2'], ['142', '5', '370', ' 109', ' 400', ' 131', '2'], ['145', '5', '367', ' 112', ' 396', ' 132', '2'], ['146', '5', '368', ' 112', ' 397', ' 133', '2'], ['148', '5', '367', ' 111', ' 397', ' 133', '2'], ['149', '5', '367', ' 111', ' 397', ' 133', '2'], ['152', '5', '369', ' 113', ' 399', ' 134', '2'], ['153', '5', '370', ' 116', ' 398', ' 135', '2'], ['154', '5', '370', ' 117', ' 398', ' 136', '2'], ['155', '5', '370', ' 118', ' 398', ' 137', '2'], ['156', '5', '370', ' 117', ' 400', ' 137', '2'], ['157', '5', '369', ' 116', ' 401', ' 138', '2'], ['158', '5', '367', ' 114', ' 401', ' 138', '2'], ['159', '5', '367', ' 114', ' 400', ' 138', '2'], ['160', '5', '368', ' 116', ' 399', ' 139', '2'], ['161', '5', '369', ' 118', ' 398', ' 140', '2'], ['162', '5', '368', ' 118', ' 398', ' 140', '2'], ['163', '5', '368', ' 118', ' 398', ' 141', '2'], ['164', '5', '367', ' 117', ' 399', ' 142', '2'], ['165', '5', '368', ' 117', ' 401', ' 143', '2'], ['166', '5', '368', ' 118', ' 400', ' 144', '2'], ['167', '5', '368', ' 117', ' 401', ' 144', '2'], ['168', '5', '368', ' 116', ' 401', ' 145', '2'], ['169', '5', '368', ' 116', ' 401', ' 145', '2'], ['170', '5', '368', ' 117', ' 401', ' 146', '2'], ['171', '5', '369', ' 118', ' 400', ' 146', '2'], ['172', '5', '370', ' 118', ' 401', ' 146', '2'], ['173', '5', '370', ' 119', ' 401', ' 147', '2'], ['176', '5', '370', ' 121', ' 402', ' 150', '2'], ['177', '5', '371', ' 124', ' 402', ' 151', '2'], ['178', '5', '372', ' 123', ' 403', ' 152', '2'], ['179', '5', '373', ' 124', ' 404', ' 153', '2'], ['180', '5', '373', ' 125', ' 404', ' 153', '2'], ['181', '5', '373', ' 126', ' 404', ' 154', '2'], ['182', '5', '373', ' 126', ' 404', ' 154', '2'], ['183', '5', '374', ' 126', ' 406', ' 155', '2'], ['184', '5', '374', ' 127', ' 405', ' 156', '2'], ['185', '5', '375', ' 128', ' 407', ' 157', '2'], ['186', '5', '374', ' 128', ' 407', ' 158', '2'], ['187', '5', '374', ' 128', ' 408', ' 158', '2'], ['188', '5', '374', ' 129', ' 408', ' 160', '2'], ['189', '5', '374', ' 130', ' 409', ' 161', '2'], ['190', '5', '375', ' 131', ' 409', ' 162', '2'], ['191', '5', '375', ' 131', ' 411', ' 164', '2'], ['192', '5', '375', ' 130', ' 412', ' 165', '2'], ['193', '5', '376', ' 131', ' 413', ' 165', '2'], ['194', '5', '376', ' 131', ' 415', ' 166', '2'], ['195', '5', '376', ' 132', ' 415', ' 168', '2'], ['196', '5', '377', ' 134', ' 415', ' 169', '2'], ['197', '5', '378', ' 135', ' 415', ' 170', '2'], ['198', '5', '378', ' 135', ' 417', ' 171', '2'], ['199', '5', '380', ' 137', ' 418', ' 172', '2'], ['200', '5', '381', ' 137', ' 419', ' 174', '2'], ['201', '5', '382', ' 138', ' 420', ' 175', '2'], ['202', '5', '383', ' 138', ' 422', ' 176', '2'], ['203', '5', '384', ' 140', ' 423', ' 177', '2'], ['204', '5', '385', ' 142', ' 423', ' 179', '2'], ['205', '5', '386', ' 143', ' 424', ' 180', '2'], ['207', '5', '387', ' 145', ' 427', ' 182', '2'], ['209', '5', '389', ' 145', ' 432', ' 186', '2'], ['210', '5', '389', ' 145', ' 432', ' 187', '2'], ['211', '5', '390', ' 147', ' 434', ' 189', '2'], ['212', '5', '391', ' 148', ' 436', ' 190', '2'], ['213', '5', '392', ' 147', ' 437', ' 191', '2'], ['214', '5', '393', ' 149', ' 439', ' 193', '2'], ['215', '5', '393', ' 151', ' 441', ' 196', '2'], ['216', '5', '394', ' 151', ' 443', ' 197', '2'], ['217', '5', '393', ' 151', ' 445', ' 200', '2'], ['218', '5', '396', ' 153', ' 447', ' 202', '2'], ['219', '5', '397', ' 156', ' 448', ' 204', '2'], ['220', '5', '399', ' 157', ' 451', ' 205', '2'], ['221', '5', '400', ' 159', ' 453', ' 208', '2'], ['222', '5', '401', ' 159', ' 455', ' 209', '2'], ['223', '5', '400', ' 159', ' 457', ' 212', '2'], ['224', '5', '401', ' 161', ' 458', ' 214', '2'], ['225', '5', '402', ' 161', ' 461', ' 217', '2'], ['226', '5', '402', ' 162', ' 463', ' 219', '2'], ['227', '5', '404', ' 163', ' 466', ' 221', '2'], ['228', '5', '407', ' 167', ' 468', ' 224', '2'], ['229', '5', '408', ' 168', ' 470', ' 227', '2'], ['230', '5', '409', ' 169', ' 473', ' 229', '2'], ['231', '5', '410', ' 170', ' 475', ' 231', '2'], ['232', '5', '412', ' 171', ' 479', ' 235', '2'], ['233', '5', '414', ' 172', ' 482', ' 237', '2'], ['234', '5', '415', ' 173', ' 485', ' 240', '2'], ['235', '5', '416', ' 174', ' 488', ' 243', '2'], ['236', '5', '419', ' 181', ' 489', ' 248', '2'], ['237', '5', '422', ' 185', ' 491', ' 251', '2'], ['238', '5', '423', ' 183', ' 496', ' 254', '2'], ['239', '5', '424', ' 184', ' 500', ' 257', '2'], ['240', '5', '428', ' 189', ' 503', ' 261', '2'], ['241', '5', '430', ' 191', ' 506', ' 265', '2'], ['242', '5', '432', ' 192', ' 511', ' 269', '2'], ['243', '5', '433', ' 194', ' 515', ' 274', '2'], ['244', '5', '435', ' 196', ' 519', ' 277', '2'], ['245', '5', '438', ' 198', ' 523', ' 280', '2'], ['246', '5', '439', ' 199', ' 528', ' 286', '2'], ['247', '5', '441', ' 201', ' 533', ' 290', '2'], ['248', '5', '444', ' 204', ' 538', ' 295', '2'], ['249', '5', '448', ' 207', ' 542', ' 300', '2'], ['250', '5', '451', ' 211', ' 546', ' 305', '2'], ['251', '5', '453', ' 215', ' 552', ' 311', '2'], ['252', '5', '454', ' 217', ' 558', ' 319', '2'], ['253', '5', '458', ' 220', ' 564', ' 324', '2'], ['254', '5', '461', ' 223', ' 571', ' 330', '2'], ['255', '5', '465', ' 226', ' 578', ' 336', '2'], ['256', '5', '469', ' 231', ' 584', ' 344', '2'], ['257', '5', '473', ' 236', ' 591', ' 351', '2'], ['258', '5', '477', ' 240', ' 599', ' 358', '2'], ['259', '5', '481', ' 243', ' 608', ' 367', '2'], ['260', '5', '485', ' 247', ' 617', ' 376', '2'], ['261', '5', '489', ' 251', ' 626', ' 386', '2'], ['262', '5', '495', ' 257', ' 636', ' 396', '2'], ['263', '5', '500', ' 264', ' 646', ' 408', '2'], ['264', '5', '508', ' 270', ' 655', ' 414', '2'], ['265', '5', '517', ' 275', ' 662', ' 416', '2'], ['266', '5', '527', ' 280', ' 670', ' 417', '2'], ['267', '5', '539', ' 286', ' 681', ' 417', '2'], ['268', '5', '555', ' 293', ' 694', ' 416', '2'], ['272', '5', '581', ' 316', ' 703', ' 416', '2'], ['273', '5', '599', ' 332', ' 708', ' 415', '2'], ['274', '5', '613', ' 344', ' 714', ' 415', '2'], ['275', '5', '628', ' 355', ' 720', ' 414', '2']]}, {'41': [['1468', '41', '341', ' 107', ' 372', ' 129', '2'], ['1469', '41', '340', ' 105', ' 373', ' 130', '2'], ['1474', '41', '342', ' 108', ' 372', ' 131', '2'], ['1475', '41', '344', ' 111', ' 371', ' 132', '2'], ['1476', '41', '345', ' 111', ' 374', ' 133', '2'], ['1477', '41', '345', ' 112', ' 374', ' 134', '2'], ['1478', '41', '346', ' 113', ' 372', ' 134', '2'], ['1479', '41', '345', ' 113', ' 373', ' 134', '2'], ['1480', '41', '345', ' 114', ' 372', ' 135', '2'], ['1481', '41', '346', ' 114', ' 372', ' 135', '2'], ['1482', '41', '346', ' 115', ' 372', ' 135', '2'], ['1483', '41', '346', ' 115', ' 373', ' 136', '2'], ['1484', '41', '346', ' 115', ' 373', ' 136', '2'], ['1488', '41', '346', ' 116', ' 376', ' 140', '2'], ['1489', '41', '346', ' 117', ' 376', ' 141', '2'], ['1490', '41', '346', ' 117', ' 375', ' 142', '2'], ['1491', '41', '347', ' 119', ' 375', ' 142', '2'], ['1492', '41', '348', ' 120', ' 376', ' 143', '2'], ['1493', '41', '346', ' 119', ' 376', ' 144', '2'], ['1494', '41', '346', ' 120', ' 376', ' 145', '2'], ['1495', '41', '347', ' 121', ' 375', ' 145', '2'], ['1496', '41', '347', ' 122', ' 376', ' 146', '2'], ['1497', '41', '348', ' 123', ' 376', ' 147', '2'], ['1498', '41', '349', ' 125', ' 375', ' 147', '2'], ['1499', '41', '351', ' 128', ' 375', ' 148', '2'], ['1500', '41', '350', ' 126', ' 377', ' 148', '2'], ['1501', '41', '350', ' 127', ' 377', ' 148', '2'], ['1502', '41', '349', ' 127', ' 378', ' 150', '2'], ['1503', '41', '348', ' 126', ' 379', ' 150', '2'], ['1504', '41', '348', ' 127', ' 379', ' 151', '2'], ['1505', '41', '347', ' 126', ' 380', ' 152', '2'], ['1506', '41', '347', ' 127', ' 381', ' 153', '2'], ['1507', '41', '347', ' 127', ' 380', ' 153', '2'], ['1508', '41', '348', ' 129', ' 381', ' 154', '2'], ['1509', '41', '348', ' 130', ' 380', ' 155', '2'], ['1510', '41', '348', ' 130', ' 381', ' 155', '2'], ['1511', '41', '348', ' 129', ' 383', ' 156', '2'], ['1512', '41', '349', ' 130', ' 384', ' 157', '2'], ['1513', '41', '348', ' 130', ' 384', ' 158', '2'], ['1514', '41', '348', ' 131', ' 384', ' 159', '2'], ['1515', '41', '348', ' 132', ' 385', ' 162', '2'], ['1516', '41', '349', ' 133', ' 387', ' 163', '2'], ['1517', '41', '349', ' 133', ' 388', ' 164', '2'], ['1518', '41', '348', ' 134', ' 388', ' 166', '2'], ['1519', '41', '348', ' 135', ' 389', ' 167', '2'], ['1520', '41', '347', ' 135', ' 388', ' 168', '2'], ['1521', '41', '347', ' 135', ' 389', ' 169', '2'], ['1522', '41', '347', ' 136', ' 388', ' 170', '2'], ['1523', '41', '346', ' 135', ' 389', ' 171', '2'], ['1524', '41', '347', ' 136', ' 389', ' 172', '2'], ['1525', '41', '347', ' 135', ' 391', ' 173', '2'], ['1526', '41', '348', ' 137', ' 391', ' 175', '2'], ['1527', '41', '348', ' 138', ' 392', ' 176', '2'], ['1528', '41', '349', ' 140', ' 392', ' 178', '2'], ['1529', '41', '349', ' 141', ' 393', ' 179', '2'], ['1530', '41', '350', ' 143', ' 392', ' 181', '2'], ['1531', '41', '349', ' 144', ' 392', ' 182', '2'], ['1532', '41', '350', ' 146', ' 393', ' 184', '2'], ['1533', '41', '349', ' 146', ' 394', ' 186', '2'], ['1534', '41', '350', ' 149', ' 394', ' 188', '2'], ['1535', '41', '351', ' 150', ' 395', ' 189', '2'], ['1536', '41', '352', ' 151', ' 396', ' 190', '2'], ['1537', '41', '353', ' 153', ' 398', ' 193', '2'], ['1538', '41', '354', ' 155', ' 399', ' 195', '2'], ['1539', '41', '354', ' 156', ' 399', ' 197', '2'], ['1540', '41', '354', ' 156', ' 401', ' 199', '2'], ['1541', '41', '354', ' 157', ' 401', ' 200', '2'], ['1542', '41', '352', ' 156', ' 402', ' 202', '2'], ['1543', '41', '353', ' 159', ' 402', ' 204', '2'], ['1544', '41', '353', ' 160', ' 403', ' 206', '2'], ['1545', '41', '353', ' 160', ' 405', ' 209', '2'], ['1546', '41', '353', ' 162', ' 405', ' 211', '2'], ['1547', '41', '353', ' 164', ' 406', ' 214', '2'], ['1548', '41', '354', ' 165', ' 408', ' 217', '2'], ['1549', '41', '353', ' 166', ' 410', ' 220', '2'], ['1550', '41', '354', ' 168', ' 411', ' 223', '2'], ['1551', '41', '354', ' 170', ' 412', ' 225', '2'], ['1552', '41', '354', ' 171', ' 413', ' 228', '2'], ['1553', '41', '356', ' 173', ' 416', ' 231', '2'], ['1554', '41', '356', ' 175', ' 418', ' 235', '2'], ['1555', '41', '356', ' 177', ' 420', ' 238', '2'], ['1556', '41', '356', ' 177', ' 422', ' 242', '2'], ['1557', '41', '356', ' 180', ' 425', ' 247', '2'], ['1558', '41', '357', ' 182', ' 426', ' 250', '2'], ['1559', '41', '359', ' 186', ' 426', ' 252', '2'], ['1560', '41', '359', ' 188', ' 429', ' 257', '2'], ['1561', '41', '360', ' 192', ' 431', ' 262', '2'], ['1562', '41', '360', ' 192', ' 433', ' 265', '2'], ['1563', '41', '360', ' 196', ' 436', ' 272', '2'], ['1564', '41', '360', ' 198', ' 438', ' 276', '2'], ['1565', '41', '362', ' 201', ' 441', ' 279', '2'], ['1566', '41', '364', ' 204', ' 444', ' 284', '2'], ['1567', '41', '368', ' 213', ' 444', ' 288', '2'], ['1568', '41', '365', ' 212', ' 449', ' 296', '2'], ['1569', '41', '365', ' 215', ' 451', ' 300', '2'], ['1570', '41', '366', ' 218', ' 455', ' 307', '2'], ['1571', '41', '368', ' 222', ' 459', ' 312', '2'], ['1572', '41', '368', ' 226', ' 463', ' 321', '2'], ['1573', '41', '369', ' 230', ' 465', ' 326', '2'], ['1574', '41', '369', ' 235', ' 470', ' 335', '2'], ['1575', '41', '370', ' 240', ' 475', ' 345', '2'], ['1576', '41', '370', ' 244', ' 479', ' 352', '2'], ['1577', '41', '371', ' 249', ' 484', ' 361', '2'], ['1578', '41', '372', ' 254', ' 490', ' 372', '2'], ['1579', '41', '373', ' 260', ' 497', ' 383', '2'], ['1580', '41', '373', ' 266', ' 505', ' 398', '2'], ['1581', '41', '374', ' 272', ' 510', ' 409', '2'], ['1582', '41', '379', ' 279', ' 514', ' 414', '2'], ['1583', '41', '385', ' 285', ' 517', ' 416', '2'], ['1584', '41', '392', ' 293', ' 520', ' 418', '2'], ['1585', '41', '401', ' 301', ' 520', ' 413', '2'], ['1586', '41', '406', ' 309', ' 520', ' 413', '2'], ['1587', '41', '412', ' 318', ' 525', ' 416', '2'], ['1588', '41', '414', ' 325', ' 522', ' 416', '2'], ['1589', '41', '421', ' 338', ' 517', ' 415', '2'], ['1590', '41', '429', ' 350', ' 517', ' 415', '2']]}, {'56': [['2359', '56', '351', ' 106', ' 374', ' 127', '2'], ['2360', '56', '351', ' 106', ' 375', ' 128', '2'], ['2361', '56', '350', ' 105', ' 376', ' 129', '2'], ['2362', '56', '350', ' 105', ' 376', ' 129', '2'], ['2363', '56', '349', ' 104', ' 376', ' 129', '2'], ['2364', '56', '350', ' 106', ' 376', ' 130', '2'], ['2365', '56', '351', ' 107', ' 376', ' 130', '2'], ['2366', '56', '351', ' 107', ' 376', ' 131', '2'], ['2367', '56', '351', ' 108', ' 376', ' 131', '2'], ['2368', '56', '351', ' 109', ' 376', ' 131', '2'], ['2369', '56', '352', ' 110', ' 375', ' 132', '2'], ['2370', '56', '352', ' 111', ' 375', ' 132', '2'], ['2371', '56', '351', ' 110', ' 376', ' 133', '2'], ['2372', '56', '351', ' 110', ' 376', ' 133', '2'], ['2373', '56', '351', ' 110', ' 377', ' 134', '2'], ['2374', '56', '351', ' 110', ' 377', ' 134', '2'], ['2375', '56', '351', ' 110', ' 377', ' 134', '2'], ['2376', '56', '351', ' 110', ' 377', ' 135', '2'], ['2377', '56', '350', ' 110', ' 378', ' 136', '2'], ['2378', '56', '350', ' 110', ' 379', ' 137', '2'], ['2379', '56', '350', ' 110', ' 379', ' 138', '2'], ['2380', '56', '350', ' 110', ' 379', ' 139', '2'], ['2381', '56', '350', ' 112', ' 379', ' 139', '2'], ['2382', '56', '350', ' 112', ' 379', ' 140', '2'], ['2383', '56', '351', ' 112', ' 379', ' 141', '2'], ['2384', '56', '352', ' 114', ' 378', ' 141', '2'], ['2385', '56', '351', ' 114', ' 379', ' 141', '2'], ['2386', '56', '352', ' 116', ' 379', ' 142', '2'], ['2387', '56', '352', ' 117', ' 379', ' 143', '2'], ['2388', '56', '352', ' 117', ' 379', ' 144', '2'], ['2389', '56', '351', ' 117', ' 379', ' 144', '2'], ['2390', '56', '350', ' 117', ' 380', ' 145', '2'], ['2391', '56', '350', ' 117', ' 380', ' 146', '2'], ['2392', '56', '350', ' 117', ' 380', ' 146', '2'], ['2393', '56', '352', ' 122', ' 378', ' 147', '2'], ['2394', '56', '350', ' 120', ' 379', ' 147', '2'], ['2395', '56', '350', ' 119', ' 380', ' 148', '2'], ['2396', '56', '350', ' 119', ' 380', ' 149', '2'], ['2397', '56', '350', ' 120', ' 381', ' 150', '2'], ['2398', '56', '351', ' 121', ' 381', ' 151', '2'], ['2401', '56', '351', ' 123', ' 382', ' 152', '2'], ['2402', '56', '352', ' 126', ' 381', ' 153', '2'], ['2403', '56', '352', ' 126', ' 382', ' 154', '2'], ['2404', '56', '352', ' 126', ' 383', ' 155', '2'], ['2405', '56', '353', ' 129', ' 384', ' 157', '2'], ['2407', '56', '352', ' 129', ' 385', ' 159', '2'], ['2408', '56', '352', ' 129', ' 386', ' 160', '2'], ['2409', '56', '351', ' 129', ' 386', ' 161', '2'], ['2410', '56', '351', ' 129', ' 387', ' 163', '2'], ['2411', '56', '350', ' 130', ' 388', ' 165', '2'], ['2412', '56', '350', ' 131', ' 388', ' 166', '2'], ['2413', '56', '349', ' 131', ' 388', ' 168', '2'], ['2414', '56', '350', ' 133', ' 388', ' 169', '2'], ['2415', '56', '350', ' 134', ' 389', ' 171', '2'], ['2416', '56', '351', ' 135', ' 389', ' 173', '2'], ['2417', '56', '350', ' 134', ' 390', ' 173', '2'], ['2418', '56', '350', ' 135', ' 389', ' 174', '2'], ['2419', '56', '350', ' 136', ' 390', ' 176', '2'], ['2420', '56', '350', ' 136', ' 391', ' 177', '2'], ['2421', '56', '350', ' 137', ' 390', ' 178', '2'], ['2422', '56', '351', ' 138', ' 391', ' 179', '2'], ['2423', '56', '351', ' 139', ' 392', ' 180', '2'], ['2424', '56', '350', ' 140', ' 392', ' 183', '2'], ['2425', '56', '350', ' 141', ' 393', ' 184', '2'], ['2426', '56', '350', ' 140', ' 394', ' 186', '2'], ['2427', '56', '350', ' 141', ' 395', ' 187', '2'], ['2428', '56', '350', ' 142', ' 396', ' 190', '2'], ['2429', '56', '352', ' 145', ' 396', ' 191', '2'], ['2430', '56', '352', ' 147', ' 396', ' 193', '2'], ['2431', '56', '352', ' 149', ' 398', ' 196', '2'], ['2432', '56', '352', ' 149', ' 398', ' 197', '2'], ['2433', '56', '352', ' 150', ' 399', ' 199', '2'], ['2434', '56', '352', ' 151', ' 401', ' 202', '2'], ['2435', '56', '353', ' 152', ' 401', ' 204', '2'], ['2436', '56', '352', ' 153', ' 402', ' 206', '2'], ['2437', '56', '352', ' 155', ' 402', ' 209', '2'], ['2438', '56', '352', ' 156', ' 403', ' 211', '2'], ['2439', '56', '352', ' 158', ' 403', ' 213', '2'], ['2440', '56', '352', ' 160', ' 405', ' 217', '2'], ['2441', '56', '352', ' 160', ' 406', ' 219', '2'], ['2442', '56', '352', ' 161', ' 407', ' 222', '2'], ['2443', '56', '352', ' 163', ' 408', ' 225', '2'], ['2444', '56', '353', ' 165', ' 409', ' 228', '2'], ['2445', '56', '354', ' 166', ' 411', ' 230', '2'], ['2446', '56', '353', ' 168', ' 412', ' 235', '2'], ['2447', '56', '353', ' 171', ' 412', ' 237', '2'], ['2448', '56', '356', ' 178', ' 413', ' 241', '2'], ['2449', '56', '356', ' 181', ' 415', ' 246', '2'], ['2450', '56', '355', ' 182', ' 418', ' 249', '2'], ['2451', '56', '355', ' 182', ' 420', ' 252', '2'], ['2452', '56', '354', ' 186', ' 422', ' 257', '2'], ['2453', '56', '356', ' 190', ' 424', ' 262', '2'], ['2454', '56', '352', ' 190', ' 426', ' 267', '2'], ['2455', '56', '353', ' 200', ' 424', ' 273', '2'], ['2456', '56', '356', ' 206', ' 425', ' 276', '2'], ['2457', '56', '354', ' 203', ' 429', ' 279', '2'], ['2458', '56', '352', ' 200', ' 434', ' 284', '2'], ['2459', '56', '351', ' 201', ' 438', ' 289', '2'], ['2460', '56', '349', ' 204', ' 441', ' 297', '2'], ['2461', '56', '350', ' 207', ' 443', ' 300', '2'], ['2462', '56', '351', ' 211', ' 446', ' 309', '2'], ['2463', '56', '352', ' 217', ' 449', ' 316', '2'], ['2464', '56', '353', ' 219', ' 454', ' 323', '2'], ['2465', '56', '358', ' 234', ' 453', ' 330', '2'], ['2466', '56', '355', ' 231', ' 461', ' 339', '2'], ['2468', '56', '355', ' 239', ' 468', ' 354', '2'], ['2469', '56', '352', ' 243', ' 473', ' 366', '2'], ['2471', '56', '351', ' 252', ' 482', ' 386', '2'], ['2472', '56', '350', ' 259', ' 489', ' 402', '2'], ['2473', '56', '352', ' 267', ' 493', ' 412', '2'], ['2474', '56', '356', ' 273', ' 495', ' 415', '2'], ['2475', '56', '362', ' 279', ' 500', ' 418', '2'], ['2479', '56', '380', ' 302', ' 497', ' 417', '2'], ['2480', '56', '389', ' 318', ' 494', ' 417', '2']]}, {'59': [['2798', '59', '354', ' 130', ' 375', ' 149', '2'], ['2802', '59', '357', ' 132', ' 380', ' 153', '2'], ['2805', '59', '355', ' 128', ' 385', ' 156', '2'], ['2806', '59', '355', ' 129', ' 385', ' 156', '2'], ['2808', '59', '353', ' 126', ' 388', ' 158', '2'], ['2810', '59', '353', ' 127', ' 388', ' 160', '2'], ['2811', '59', '354', ' 128', ' 390', ' 161', '2'], ['2812', '59', '354', ' 130', ' 390', ' 163', '2'], ['2815', '59', '355', ' 131', ' 394', ' 166', '2'], ['2818', '59', '357', ' 134', ' 396', ' 170', '2'], ['2819', '59', '357', ' 134', ' 397', ' 172', '2'], ['2820', '59', '358', ' 135', ' 398', ' 173', '2'], ['2821', '59', '360', ' 138', ' 398', ' 174', '2'], ['2822', '59', '360', ' 137', ' 400', ' 175', '2'], ['2823', '59', '360', ' 138', ' 401', ' 176', '2'], ['2824', '59', '362', ' 142', ' 401', ' 179', '2'], ['2825', '59', '363', ' 144', ' 401', ' 181', '2'], ['2826', '59', '362', ' 143', ' 403', ' 182', '2'], ['2827', '59', '363', ' 144', ' 404', ' 184', '2'], ['2828', '59', '363', ' 144', ' 406', ' 186', '2'], ['2829', '59', '364', ' 144', ' 407', ' 187', '2'], ['2830', '59', '365', ' 145', ' 409', ' 189', '2'], ['2831', '59', '366', ' 146', ' 410', ' 190', '2'], ['2832', '59', '368', ' 149', ' 411', ' 192', '2'], ['2833', '59', '367', ' 148', ' 412', ' 194', '2'], ['2834', '59', '367', ' 149', ' 414', ' 196', '2'], ['2835', '59', '368', ' 151', ' 414', ' 198', '2'], ['2836', '59', '370', ' 154', ' 415', ' 199', '2'], ['2837', '59', '370', ' 154', ' 417', ' 201', '2'], ['2838', '59', '372', ' 157', ' 418', ' 204', '2'], ['2839', '59', '373', ' 159', ' 420', ' 207', '2'], ['2840', '59', '375', ' 162', ' 421', ' 209', '2'], ['2841', '59', '375', ' 162', ' 423', ' 211', '2'], ['2842', '59', '375', ' 164', ' 424', ' 213', '2'], ['2843', '59', '376', ' 164', ' 428', ' 216', '2'], ['2844', '59', '375', ' 162', ' 432', ' 219', '2'], ['2845', '59', '377', ' 167', ' 432', ' 222', '2'], ['2846', '59', '379', ' 170', ' 434', ' 226', '2'], ['2847', '59', '379', ' 172', ' 435', ' 228', '2'], ['2848', '59', '382', ' 177', ' 437', ' 231', '2'], ['2849', '59', '384', ' 179', ' 440', ' 234', '2'], ['2850', '59', '385', ' 180', ' 443', ' 237', '2'], ['2851', '59', '385', ' 183', ' 444', ' 240', '2'], ['2852', '59', '387', ' 185', ' 448', ' 244', '2'], ['2853', '59', '385', ' 180', ' 455', ' 249', '2'], ['2854', '59', '387', ' 183', ' 458', ' 253', '2'], ['2855', '59', '387', ' 182', ' 462', ' 256', '2'], ['2856', '59', '393', ' 192', ' 461', ' 260', '2'], ['2857', '59', '391', ' 189', ' 468', ' 265', '2'], ['2858', '59', '394', ' 194', ' 470', ' 270', '2'], ['2859', '59', '397', ' 203', ' 471', ' 275', '2'], ['2860', '59', '401', ' 208', ' 475', ' 280', '2'], ['2861', '59', '399', ' 203', ' 483', ' 286', '2'], ['2862', '59', '398', ' 200', ' 489', ' 290', '2'], ['2863', '59', '399', ' 201', ' 494', ' 296', '2'], ['2864', '59', '401', ' 203', ' 499', ' 301', '2'], ['2865', '59', '403', ' 206', ' 504', ' 308', '2'], ['2866', '59', '407', ' 210', ' 509', ' 314', '2'], ['2867', '59', '409', ' 214', ' 514', ' 322', '2'], ['2868', '59', '413', ' 218', ' 520', ' 329', '2'], ['2869', '59', '416', ' 221', ' 526', ' 335', '2'], ['2870', '59', '419', ' 224', ' 532', ' 342', '2'], ['2871', '59', '423', ' 232', ' 538', ' 351', '2'], ['2872', '59', '428', ' 238', ' 545', ' 360', '2'], ['2873', '59', '430', ' 242', ' 554', ' 372', '2'], ['2874', '59', '434', ' 247', ' 563', ' 382', '2'], ['2875', '59', '435', ' 252', ' 576', ' 401', '2'], ['2876', '59', '441', ' 259', ' 585', ' 410', '2'], ['2877', '59', '449', ' 266', ' 591', ' 415', '2'], ['2878', '59', '458', ' 273', ' 597', ' 417', '2'], ['2879', '59', '469', ' 280', ' 606', ' 419', '2'], ['2880', '59', '482', ' 289', ' 614', ' 417', '2'], ['3090', '59', '573', ' 235', ' 617', ' 277', '3'], ['3091', '59', '569', ' 220', ' 620', ' 270', '3'], ['3092', '59', '574', ' 222', ' 621', ' 268', '3'], ['3093', '59', '578', ' 223', ' 622', ' 268', '3'], ['3094', '59', '584', ' 230', ' 626', ' 274', '3'], ['3097', '59', '601', ' 249', ' 638', ' 288', '3'], ['3098', '59', '604', ' 253', ' 641', ' 292', '3'], ['3101', '59', '615', ' 263', ' 652', ' 301', '3']]}, {'78': [['3587', '78', '342', ' 107', ' 366', ' 127', '2'], ['3588', '78', '342', ' 108', ' 366', ' 128', '2'], ['3589', '78', '343', ' 109', ' 366', ' 128', '2'], ['3590', '78', '343', ' 109', ' 367', ' 129', '2'], ['3591', '78', '343', ' 109', ' 366', ' 129', '2'], ['3592', '78', '342', ' 110', ' 366', ' 129', '2'], ['3593', '78', '342', ' 110', ' 365', ' 130', '2'], ['3594', '78', '342', ' 111', ' 365', ' 129', '2'], ['3595', '78', '343', ' 112', ' 365', ' 130', '2'], ['3596', '78', '343', ' 113', ' 365', ' 130', '2'], ['3597', '78', '343', ' 113', ' 366', ' 130', '2'], ['3598', '78', '343', ' 113', ' 366', ' 131', '2'], ['3599', '78', '343', ' 113', ' 367', ' 131', '2'], ['3600', '78', '342', ' 112', ' 367', ' 132', '2'], ['3601', '78', '343', ' 113', ' 368', ' 132', '2'], ['3602', '78', '344', ' 114', ' 368', ' 133', '2'], ['3603', '78', '344', ' 115', ' 368', ' 134', '2'], ['3604', '78', '344', ' 115', ' 368', ' 134', '2'], ['3605', '78', '344', ' 116', ' 368', ' 135', '2'], ['3606', '78', '345', ' 117', ' 368', ' 135', '2'], ['3607', '78', '345', ' 118', ' 369', ' 137', '2'], ['3608', '78', '344', ' 118', ' 369', ' 138', '2'], ['3609', '78', '343', ' 119', ' 369', ' 138', '2'], ['3610', '78', '343', ' 119', ' 369', ' 139', '2'], ['3611', '78', '344', ' 119', ' 370', ' 139', '2'], ['3612', '78', '344', ' 121', ' 370', ' 141', '2'], ['3613', '78', '345', ' 123', ' 370', ' 142', '2'], ['3614', '78', '344', ' 122', ' 371', ' 142', '2'], ['3615', '78', '344', ' 122', ' 371', ' 142', '2'], ['3616', '78', '344', ' 122', ' 372', ' 143', '2'], ['3617', '78', '344', ' 123', ' 372', ' 144', '2'], ['3618', '78', '344', ' 125', ' 371', ' 145', '2'], ['3619', '78', '343', ' 125', ' 371', ' 146', '2'], ['3620', '78', '343', ' 126', ' 372', ' 147', '2'], ['3621', '78', '344', ' 127', ' 372', ' 147', '2'], ['3622', '78', '345', ' 128', ' 372', ' 147', '2'], ['3623', '78', '345', ' 128', ' 373', ' 148', '2'], ['3624', '78', '345', ' 128', ' 373', ' 148', '2'], ['3625', '78', '343', ' 128', ' 373', ' 149', '2'], ['3626', '78', '343', ' 127', ' 375', ' 150', '2'], ['3627', '78', '342', ' 127', ' 374', ' 151', '2'], ['3628', '78', '342', ' 128', ' 375', ' 152', '2'], ['3629', '78', '342', ' 128', ' 376', ' 153', '2'], ['3630', '78', '342', ' 128', ' 376', ' 154', '2'], ['3631', '78', '342', ' 129', ' 377', ' 154', '2'], ['3632', '78', '342', ' 130', ' 375', ' 155', '2'], ['3633', '78', '342', ' 131', ' 376', ' 156', '2'], ['3634', '78', '342', ' 131', ' 376', ' 156', '2'], ['3635', '78', '341', ' 131', ' 377', ' 157', '2'], ['3636', '78', '342', ' 133', ' 376', ' 158', '2'], ['3637', '78', '342', ' 133', ' 377', ' 160', '2'], ['3638', '78', '343', ' 135', ' 378', ' 161', '2'], ['3639', '78', '343', ' 135', ' 379', ' 163', '2'], ['3640', '78', '343', ' 136', ' 380', ' 164', '2'], ['3641', '78', '343', ' 139', ' 377', ' 165', '2'], ['3642', '78', '342', ' 138', ' 379', ' 166', '2'], ['3643', '78', '341', ' 139', ' 378', ' 168', '2'], ['3644', '78', '341', ' 140', ' 379', ' 169', '2'], ['3645', '78', '341', ' 141', ' 379', ' 170', '2'], ['3646', '78', '340', ' 141', ' 379', ' 171', '2'], ['3647', '78', '341', ' 142', ' 380', ' 172', '2'], ['3648', '78', '342', ' 143', ' 381', ' 173', '2'], ['3649', '78', '343', ' 144', ' 382', ' 175', '2'], ['3650', '78', '343', ' 145', ' 383', ' 176', '2'], ['3651', '78', '343', ' 146', ' 384', ' 178', '2'], ['3652', '78', '342', ' 147', ' 384', ' 180', '2'], ['3653', '78', '342', ' 147', ' 383', ' 180', '2'], ['3654', '78', '342', ' 149', ' 383', ' 181', '2'], ['3655', '78', '341', ' 150', ' 385', ' 184', '2'], ['3656', '78', '341', ' 149', ' 386', ' 185', '2'], ['3657', '78', '342', ' 150', ' 387', ' 187', '2'], ['3658', '78', '340', ' 151', ' 388', ' 189', '2'], ['3659', '78', '341', ' 153', ' 388', ' 191', '2'], ['3660', '78', '342', ' 156', ' 388', ' 193', '2'], ['3661', '78', '342', ' 157', ' 389', ' 196', '2'], ['3662', '78', '343', ' 159', ' 390', ' 197', '2'], ['3663', '78', '344', ' 161', ' 390', ' 199', '2'], ['3664', '78', '343', ' 162', ' 391', ' 201', '2'], ['3665', '78', '344', ' 163', ' 392', ' 204', '2'], ['3666', '78', '344', ' 165', ' 392', ' 206', '2'], ['3667', '78', '344', ' 166', ' 393', ' 209', '2'], ['3668', '78', '344', ' 167', ' 393', ' 210', '2'], ['3669', '78', '344', ' 169', ' 394', ' 213', '2'], ['3670', '78', '345', ' 172', ' 394', ' 215', '2'], ['3671', '78', '344', ' 173', ' 395', ' 218', '2'], ['3672', '78', '344', ' 175', ' 396', ' 222', '2'], ['3673', '78', '344', ' 177', ' 397', ' 225', '2'], ['3674', '78', '344', ' 179', ' 398', ' 227', '2'], ['3675', '78', '344', ' 180', ' 400', ' 230', '2'], ['3676', '78', '345', ' 183', ' 401', ' 235', '2'], ['3677', '78', '345', ' 185', ' 403', ' 237', '2'], ['3678', '78', '345', ' 186', ' 405', ' 241', '2'], ['3679', '78', '346', ' 189', ' 406', ' 244', '2'], ['3680', '78', '346', ' 192', ' 406', ' 248', '2'], ['3681', '78', '345', ' 194', ' 409', ' 252', '2'], ['3682', '78', '344', ' 196', ' 410', ' 257', '2'], ['3683', '78', '344', ' 198', ' 412', ' 262', '2'], ['3684', '78', '344', ' 202', ' 413', ' 266', '2'], ['3685', '78', '344', ' 205', ' 415', ' 270', '2'], ['3686', '78', '345', ' 208', ' 417', ' 275', '2'], ['3687', '78', '345', ' 211', ' 419', ' 280', '2'], ['3688', '78', '345', ' 216', ' 420', ' 286', '2'], ['3689', '78', '345', ' 219', ' 423', ' 292', '2'], ['3690', '78', '344', ' 222', ' 425', ' 297', '2'], ['3691', '78', '344', ' 225', ' 427', ' 303', '2'], ['3692', '78', '344', ' 229', ' 429', ' 309', '2'], ['3693', '78', '344', ' 233', ' 433', ' 316', '2'], ['3694', '78', '345', ' 238', ' 436', ' 323', '2'], ['3695', '78', '347', ' 242', ' 439', ' 329', '2'], ['3696', '78', '347', ' 247', ' 442', ' 337', '2'], ['3697', '78', '346', ' 252', ' 446', ' 347', '2'], ['3698', '78', '346', ' 257', ' 448', ' 354', '2'], ['3699', '78', '346', ' 264', ' 452', ' 364', '2'], ['3700', '78', '344', ' 269', ' 455', ' 374', '2'], ['3701', '78', '343', ' 275', ' 460', ' 386', '2'], ['3702', '78', '341', ' 281', ' 466', ' 399', '2'], ['3703', '78', '341', ' 288', ' 468', ' 410', '2'], ['3704', '78', '345', ' 296', ' 471', ' 416', '2'], ['3705', '78', '350', ' 302', ' 472', ' 417', '2'], ['3706', '78', '358', ' 313', ' 472', ' 417', '2'], ['3707', '78', '366', ' 322', ' 471', ' 415', '2'], ['3708', '78', '372', ' 332', ' 471', ' 416', '2'], ['3709', '78', '379', ' 344', ' 468', ' 415', '2'], ['3710', '78', '387', ' 356', ' 464', ' 414', '2']]}, {'77': [['3541', '77', '374', ' 106', ' 396', ' 120', '2'], ['3542', '77', '374', ' 107', ' 397', ' 121', '2'], ['3543', '77', '373', ' 106', ' 397', ' 122', '2'], ['3546', '77', '374', ' 107', ' 398', ' 123', '2'], ['3547', '77', '374', ' 108', ' 399', ' 124', '2'], ['3548', '77', '375', ' 108', ' 398', ' 124', '2'], ['3549', '77', '374', ' 108', ' 399', ' 124', '2'], ['3550', '77', '374', ' 108', ' 399', ' 124', '2'], ['3553', '77', '373', ' 108', ' 400', ' 126', '2'], ['3554', '77', '373', ' 108', ' 400', ' 126', '2'], ['3555', '77', '373', ' 109', ' 400', ' 127', '2'], ['3556', '77', '374', ' 109', ' 400', ' 127', '2'], ['3557', '77', '375', ' 109', ' 401', ' 127', '2'], ['3558', '77', '376', ' 110', ' 402', ' 127', '2'], ['3559', '77', '377', ' 110', ' 402', ' 127', '2'], ['3560', '77', '377', ' 111', ' 402', ' 127', '2'], ['3561', '77', '378', ' 111', ' 402', ' 128', '2'], ['3562', '77', '378', ' 112', ' 403', ' 128', '2'], ['3567', '77', '379', ' 112', ' 404', ' 128', '2'], ['3568', '77', '380', ' 112', ' 405', ' 129', '2'], ['3569', '77', '380', ' 113', ' 405', ' 129', '2'], ['3570', '77', '381', ' 113', ' 405', ' 129', '2'], ['3571', '77', '381', ' 113', ' 406', ' 129', '2'], ['3573', '77', '381', ' 114', ' 406', ' 130', '2'], ['3574', '77', '381', ' 114', ' 407', ' 131', '2'], ['3575', '77', '381', ' 114', ' 407', ' 131', '2'], ['3576', '77', '381', ' 114', ' 408', ' 131', '2'], ['3577', '77', '381', ' 113', ' 409', ' 131', '2'], ['3578', '77', '380', ' 113', ' 409', ' 132', '2'], ['3579', '77', '380', ' 112', ' 409', ' 132', '2'], ['3580', '77', '381', ' 112', ' 409', ' 132', '2'], ['3581', '77', '381', ' 112', ' 409', ' 132', '2'], ['3582', '77', '382', ' 113', ' 409', ' 132', '2'], ['3583', '77', '382', ' 113', ' 410', ' 132', '2'], ['3584', '77', '382', ' 113', ' 410', ' 133', '2'], ['3585', '77', '383', ' 113', ' 411', ' 133', '2'], ['3586', '77', '383', ' 113', ' 411', ' 133', '2'], ['3587', '77', '384', ' 113', ' 411', ' 133', '2'], ['3588', '77', '384', ' 114', ' 411', ' 133', '2'], ['3589', '77', '384', ' 114', ' 411', ' 134', '2'], ['3590', '77', '385', ' 115', ' 411', ' 134', '2'], ['3591', '77', '385', ' 115', ' 411', ' 134', '2'], ['3592', '77', '386', ' 116', ' 412', ' 135', '2'], ['3593', '77', '387', ' 117', ' 411', ' 135', '2'], ['3594', '77', '388', ' 117', ' 412', ' 135', '2'], ['3595', '77', '388', ' 118', ' 413', ' 136', '2'], ['3596', '77', '388', ' 119', ' 413', ' 137', '2'], ['3597', '77', '388', ' 119', ' 415', ' 138', '2'], ['3598', '77', '387', ' 119', ' 415', ' 139', '2'], ['3599', '77', '388', ' 119', ' 415', ' 139', '2'], ['3600', '77', '389', ' 120', ' 415', ' 139', '2'], ['3601', '77', '389', ' 120', ' 415', ' 139', '2'], ['3602', '77', '389', ' 120', ' 416', ' 139', '2'], ['3603', '77', '390', ' 120', ' 417', ' 140', '2'], ['3604', '77', '390', ' 120', ' 417', ' 140', '2'], ['3605', '77', '391', ' 120', ' 417', ' 140', '2'], ['3606', '77', '391', ' 121', ' 417', ' 140', '2'], ['3607', '77', '392', ' 121', ' 417', ' 140', '2'], ['3608', '77', '392', ' 121', ' 417', ' 140', '2'], ['3609', '77', '392', ' 121', ' 417', ' 140', '2'], ['3610', '77', '391', ' 121', ' 419', ' 141', '2'], ['3611', '77', '392', ' 121', ' 420', ' 142', '2'], ['3612', '77', '392', ' 121', ' 421', ' 142', '2'], ['3613', '77', '393', ' 122', ' 421', ' 143', '2'], ['3614', '77', '393', ' 122', ' 421', ' 143', '2'], ['3615', '77', '393', ' 122', ' 422', ' 144', '2'], ['3616', '77', '394', ' 124', ' 422', ' 145', '2'], ['3617', '77', '395', ' 125', ' 422', ' 145', '2'], ['3618', '77', '395', ' 125', ' 423', ' 145', '2'], ['3619', '77', '395', ' 125', ' 423', ' 146', '2'], ['3620', '77', '394', ' 125', ' 423', ' 147', '2'], ['3621', '77', '395', ' 125', ' 424', ' 147', '2'], ['3622', '77', '396', ' 126', ' 423', ' 147', '2'], ['3623', '77', '396', ' 127', ' 424', ' 147', '2'], ['3624', '77', '396', ' 127', ' 424', ' 147', '2'], ['3625', '77', '396', ' 127', ' 424', ' 147', '2'], ['3626', '77', '396', ' 127', ' 425', ' 148', '2'], ['3627', '77', '396', ' 128', ' 425', ' 149', '2'], ['3628', '77', '397', ' 129', ' 426', ' 149', '2'], ['3629', '77', '396', ' 129', ' 427', ' 150', '2'], ['3630', '77', '397', ' 129', ' 428', ' 151', '2'], ['3631', '77', '397', ' 129', ' 429', ' 151', '2'], ['3632', '77', '398', ' 130', ' 429', ' 152', '2'], ['3633', '77', '398', ' 131', ' 429', ' 152', '2'], ['3634', '77', '399', ' 131', ' 430', ' 152', '2'], ['3635', '77', '398', ' 131', ' 431', ' 153', '2'], ['3636', '77', '399', ' 131', ' 432', ' 154', '2'], ['3637', '77', '399', ' 131', ' 432', ' 153', '2'], ['3638', '77', '399', ' 131', ' 433', ' 154', '2'], ['3639', '77', '399', ' 131', ' 434', ' 154', '2'], ['3640', '77', '399', ' 131', ' 434', ' 155', '2'], ['3641', '77', '400', ' 131', ' 435', ' 155', '2'], ['3642', '77', '400', ' 132', ' 435', ' 156', '2'], ['3643', '77', '401', ' 133', ' 434', ' 156', '2'], ['3644', '77', '402', ' 134', ' 434', ' 156', '2'], ['3645', '77', '401', ' 133', ' 436', ' 157', '2'], ['3646', '77', '401', ' 133', ' 435', ' 157', '2'], ['3647', '77', '402', ' 134', ' 436', ' 158', '2'], ['3648', '77', '402', ' 135', ' 437', ' 159', '2'], ['3649', '77', '403', ' 136', ' 437', ' 159', '2'], ['3650', '77', '403', ' 136', ' 438', ' 160', '2'], ['3651', '77', '404', ' 136', ' 440', ' 161', '2'], ['3652', '77', '403', ' 136', ' 442', ' 163', '2'], ['3653', '77', '403', ' 136', ' 444', ' 163', '2'], ['3654', '77', '403', ' 136', ' 445', ' 165', '2'], ['3655', '77', '404', ' 138', ' 445', ' 166', '2'], ['3656', '77', '405', ' 138', ' 445', ' 167', '2'], ['3657', '77', '405', ' 139', ' 445', ' 167', '2'], ['3658', '77', '406', ' 140', ' 446', ' 168', '2'], ['3659', '77', '405', ' 140', ' 446', ' 168', '2'], ['3660', '77', '405', ' 140', ' 446', ' 168', '2'], ['3661', '77', '406', ' 140', ' 447', ' 170', '2'], ['3662', '77', '407', ' 140', ' 448', ' 170', '2'], ['3663', '77', '406', ' 140', ' 449', ' 171', '2'], ['3664', '77', '407', ' 141', ' 449', ' 172', '2'], ['3665', '77', '408', ' 142', ' 450', ' 173', '2'], ['3666', '77', '409', ' 143', ' 449', ' 173', '2'], ['3667', '77', '410', ' 144', ' 449', ' 173', '2'], ['3668', '77', '410', ' 145', ' 448', ' 173', '2'], ['3669', '77', '410', ' 146', ' 448', ' 174', '2'], ['3670', '77', '410', ' 146', ' 450', ' 175', '2'], ['3671', '77', '411', ' 146', ' 452', ' 176', '2'], ['3672', '77', '411', ' 147', ' 453', ' 177', '2'], ['3673', '77', '411', ' 147', ' 454', ' 178', '2'], ['3674', '77', '412', ' 148', ' 457', ' 181', '2'], ['3675', '77', '412', ' 148', ' 457', ' 181', '2'], ['3676', '77', '411', ' 149', ' 458', ' 183', '2'], ['3677', '77', '411', ' 149', ' 457', ' 183', '2'], ['3678', '77', '410', ' 149', ' 457', ' 184', '2'], ['3679', '77', '411', ' 150', ' 457', ' 184', '2'], ['3680', '77', '413', ' 151', ' 457', ' 184', '2'], ['3681', '77', '414', ' 152', ' 459', ' 185', '2'], ['3682', '77', '414', ' 152', ' 459', ' 186', '2'], ['3683', '77', '415', ' 153', ' 460', ' 187', '2'], ['3684', '77', '416', ' 154', ' 462', ' 188', '2'], ['3685', '77', '416', ' 155', ' 463', ' 190', '2'], ['3686', '77', '417', ' 155', ' 463', ' 191', '2'], ['3687', '77', '418', ' 157', ' 463', ' 191', '2'], ['3688', '77', '418', ' 157', ' 463', ' 192', '2'], ['3689', '77', '419', ' 158', ' 464', ' 194', '2'], ['3690', '77', '419', ' 159', ' 466', ' 195', '2'], ['3691', '77', '420', ' 160', ' 466', ' 197', '2'], ['3692', '77', '420', ' 161', ' 467', ' 198', '2'], ['3693', '77', '419', ' 161', ' 469', ' 199', '2'], ['3694', '77', '420', ' 163', ' 470', ' 202', '2'], ['3695', '77', '420', ' 163', ' 471', ' 203', '2'], ['3696', '77', '421', ' 164', ' 472', ' 204', '2'], ['3697', '77', '421', ' 164', ' 473', ' 205', '2'], ['3698', '77', '421', ' 165', ' 474', ' 206', '2'], ['3699', '77', '422', ' 167', ' 474', ' 207', '2'], ['3700', '77', '423', ' 167', ' 476', ' 209', '2'], ['3701', '77', '424', ' 167', ' 478', ' 210', '2'], ['3702', '77', '425', ' 169', ' 478', ' 210', '2'], ['3703', '77', '426', ' 170', ' 479', ' 212', '2'], ['3704', '77', '426', ' 171', ' 480', ' 214', '2'], ['3705', '77', '426', ' 173', ' 480', ' 215', '2'], ['3706', '77', '426', ' 173', ' 481', ' 217', '2'], ['3707', '77', '426', ' 173', ' 482', ' 218', '2'], ['3708', '77', '426', ' 175', ' 482', ' 220', '2'], ['3709', '77', '427', ' 176', ' 484', ' 222', '2'], ['3710', '77', '429', ' 178', ' 486', ' 224', '2'], ['3711', '77', '430', ' 179', ' 487', ' 225', '2'], ['3712', '77', '431', ' 180', ' 488', ' 227', '2'], ['3713', '77', '432', ' 180', ' 490', ' 228', '2'], ['3714', '77', '433', ' 181', ' 492', ' 230', '2'], ['3715', '77', '433', ' 183', ' 493', ' 232', '2'], ['3716', '77', '434', ' 184', ' 494', ' 234', '2'], ['3717', '77', '434', ' 186', ' 495', ' 236', '2'], ['3718', '77', '436', ' 188', ' 497', ' 238', '2'], ['3719', '77', '438', ' 191', ' 499', ' 241', '2'], ['3720', '77', '438', ' 191', ' 501', ' 244', '2'], ['3721', '77', '438', ' 192', ' 503', ' 246', '2'], ['3722', '77', '438', ' 193', ' 505', ' 248', '2'], ['3723', '77', '439', ' 195', ' 506', ' 250', '2'], ['3724', '77', '440', ' 196', ' 509', ' 253', '2'], ['3725', '77', '440', ' 198', ' 510', ' 255', '2'], ['3726', '77', '441', ' 200', ' 511', ' 258', '2'], ['3727', '77', '441', ' 201', ' 513', ' 260', '2'], ['3728', '77', '443', ' 202', ' 515', ' 262', '2'], ['3729', '77', '444', ' 203', ' 519', ' 266', '2'], ['3730', '77', '444', ' 205', ' 521', ' 270', '2'], ['3731', '77', '446', ' 207', ' 524', ' 274', '2'], ['3732', '77', '447', ' 210', ' 525', ' 276', '2'], ['3733', '77', '449', ' 213', ' 526', ' 278', '2'], ['3734', '77', '451', ' 215', ' 529', ' 281', '2'], ['3735', '77', '452', ' 218', ' 531', ' 286', '2'], ['3736', '77', '453', ' 220', ' 534', ' 289', '2'], ['3737', '77', '454', ' 221', ' 537', ' 292', '2'], ['3738', '77', '454', ' 223', ' 539', ' 296', '2'], ['3739', '77', '456', ' 225', ' 543', ' 300', '2'], ['3740', '77', '457', ' 227', ' 545', ' 303', '2'], ['3741', '77', '459', ' 230', ' 549', ' 309', '2'], ['3742', '77', '461', ' 233', ' 552', ' 312', '2'], ['3743', '77', '464', ' 236', ' 554', ' 315', '2'], ['3744', '77', '466', ' 240', ' 558', ' 320', '2'], ['3745', '77', '468', ' 242', ' 561', ' 323', '2'], ['3746', '77', '470', ' 246', ' 565', ' 329', '2'], ['3747', '77', '471', ' 249', ' 569', ' 334', '2'], ['3748', '77', '474', ' 252', ' 573', ' 338', '2'], ['3749', '77', '475', ' 255', ' 578', ' 345', '2'], ['3750', '77', '476', ' 258', ' 582', ' 350', '2'], ['3751', '77', '479', ' 262', ' 586', ' 355', '2'], ['3752', '77', '482', ' 267', ' 591', ' 361', '2'], ['3753', '77', '483', ' 270', ' 596', ' 368', '2'], ['3754', '77', '486', ' 274', ' 601', ' 374', '2'], ['3755', '77', '488', ' 278', ' 607', ' 382', '2'], ['3756', '77', '490', ' 281', ' 612', ' 387', '2'], ['3757', '77', '492', ' 286', ' 618', ' 397', '2'], ['3758', '77', '494', ' 292', ' 625', ' 406', '2'], ['3759', '77', '499', ' 296', ' 630', ' 411', '2'], ['3760', '77', '504', ' 300', ' 635', ' 415', '2'], ['3761', '77', '511', ' 306', ' 638', ' 416', '2'], ['3762', '77', '517', ' 312', ' 639', ' 415', '2'], ['3763', '77', '526', ' 317', ' 647', ' 416', '2'], ['3764', '77', '530', ' 322', ' 649', ' 417', '2'], ['3765', '77', '535', ' 328', ' 650', ' 417', '2'], ['3766', '77', '540', ' 334', ' 650', ' 416', '2']]}, {'89': [['3663', '89', '371', ' 109', ' 394', ' 124', '2'], ['3665', '89', '372', ' 109', ' 395', ' 125', '2'], ['3666', '89', '372', ' 109', ' 395', ' 125', '2'], ['3667', '89', '372', ' 109', ' 395', ' 125', '2'], ['3668', '89', '372', ' 109', ' 395', ' 125', '2'], ['3669', '89', '371', ' 108', ' 397', ' 126', '2'], ['3670', '89', '371', ' 108', ' 397', ' 126', '2'], ['3671', '89', '372', ' 108', ' 397', ' 126', '2'], ['3672', '89', '373', ' 109', ' 397', ' 126', '2'], ['3673', '89', '374', ' 110', ' 397', ' 126', '2'], ['3674', '89', '374', ' 111', ' 398', ' 127', '2'], ['3675', '89', '375', ' 111', ' 399', ' 127', '2'], ['3676', '89', '374', ' 110', ' 399', ' 128', '2'], ['3677', '89', '374', ' 110', ' 400', ' 128', '2'], ['3678', '89', '375', ' 110', ' 399', ' 128', '2'], ['3679', '89', '375', ' 111', ' 399', ' 128', '2'], ['3680', '89', '375', ' 110', ' 400', ' 128', '2'], ['3681', '89', '375', ' 110', ' 401', ' 128', '2'], ['3682', '89', '376', ' 110', ' 401', ' 129', '2'], ['3685', '89', '376', ' 112', ' 402', ' 131', '2'], ['3686', '89', '376', ' 113', ' 402', ' 131', '2'], ['3687', '89', '376', ' 113', ' 402', ' 131', '2'], ['3688', '89', '377', ' 114', ' 402', ' 132', '2'], ['3689', '89', '377', ' 114', ' 402', ' 132', '2'], ['3690', '89', '377', ' 113', ' 403', ' 132', '2'], ['3691', '89', '378', ' 114', ' 404', ' 133', '2'], ['3692', '89', '378', ' 113', ' 405', ' 133', '2'], ['3693', '89', '379', ' 114', ' 406', ' 134', '2'], ['3694', '89', '380', ' 116', ' 405', ' 134', '2'], ['3695', '89', '380', ' 118', ' 404', ' 134', '2'], ['3696', '89', '381', ' 118', ' 404', ' 134', '2'], ['3697', '89', '381', ' 118', ' 405', ' 134', '2'], ['3698', '89', '381', ' 118', ' 406', ' 135', '2'], ['3699', '89', '381', ' 118', ' 407', ' 135', '2'], ['3700', '89', '381', ' 118', ' 407', ' 135', '2'], ['3701', '89', '381', ' 117', ' 408', ' 135', '2'], ['3702', '89', '381', ' 118', ' 408', ' 136', '2'], ['3703', '89', '381', ' 118', ' 409', ' 137', '2'], ['3704', '89', '381', ' 118', ' 409', ' 137', '2'], ['3705', '89', '381', ' 118', ' 410', ' 138', '2'], ['3706', '89', '381', ' 119', ' 410', ' 138', '2'], ['3707', '89', '381', ' 118', ' 410', ' 137', '2'], ['3708', '89', '382', ' 117', ' 411', ' 137', '2'], ['3709', '89', '382', ' 118', ' 411', ' 138', '2'], ['3710', '89', '383', ' 118', ' 411', ' 138', '2'], ['3711', '89', '383', ' 118', ' 412', ' 139', '2'], ['3712', '89', '384', ' 119', ' 412', ' 139', '2'], ['3713', '89', '385', ' 120', ' 412', ' 139', '2'], ['3714', '89', '385', ' 120', ' 412', ' 139', '2'], ['3715', '89', '385', ' 121', ' 411', ' 140', '2'], ['3716', '89', '385', ' 120', ' 412', ' 140', '2'], ['3717', '89', '385', ' 120', ' 412', ' 141', '2'], ['3718', '89', '385', ' 121', ' 412', ' 142', '2'], ['3719', '89', '385', ' 121', ' 412', ' 142', '2'], ['3720', '89', '386', ' 122', ' 413', ' 143', '2'], ['3721', '89', '387', ' 123', ' 413', ' 144', '2'], ['3722', '89', '387', ' 123', ' 414', ' 144', '2'], ['3723', '89', '387', ' 122', ' 415', ' 145', '2'], ['3724', '89', '386', ' 123', ' 415', ' 145', '2'], ['3725', '89', '386', ' 123', ' 415', ' 146', '2'], ['3726', '89', '387', ' 123', ' 415', ' 146', '2'], ['3727', '89', '388', ' 124', ' 416', ' 146', '2'], ['3728', '89', '389', ' 125', ' 416', ' 147', '2'], ['3729', '89', '390', ' 126', ' 416', ' 147', '2'], ['3730', '89', '390', ' 127', ' 416', ' 147', '2'], ['3731', '89', '391', ' 128', ' 418', ' 149', '2'], ['3732', '89', '390', ' 128', ' 419', ' 150', '2'], ['3733', '89', '390', ' 128', ' 419', ' 151', '2'], ['3734', '89', '390', ' 129', ' 421', ' 152', '2'], ['3735', '89', '391', ' 130', ' 422', ' 153', '2'], ['3736', '89', '391', ' 129', ' 424', ' 154', '2'], ['3737', '89', '391', ' 129', ' 423', ' 154', '2'], ['3738', '89', '391', ' 129', ' 424', ' 154', '2'], ['3739', '89', '391', ' 129', ' 424', ' 155', '2'], ['3740', '89', '391', ' 130', ' 424', ' 155', '2'], ['3741', '89', '392', ' 130', ' 425', ' 156', '2'], ['3742', '89', '392', ' 131', ' 425', ' 157', '2'], ['3743', '89', '393', ' 132', ' 425', ' 157', '2'], ['3744', '89', '393', ' 133', ' 425', ' 158', '2'], ['3745', '89', '393', ' 134', ' 424', ' 159', '2'], ['3746', '89', '393', ' 135', ' 425', ' 160', '2'], ['3747', '89', '394', ' 135', ' 426', ' 160', '2'], ['3748', '89', '395', ' 136', ' 427', ' 161', '2'], ['3749', '89', '396', ' 136', ' 429', ' 162', '2'], ['3750', '89', '396', ' 136', ' 431', ' 163', '2'], ['3751', '89', '396', ' 137', ' 432', ' 165', '2'], ['3752', '89', '395', ' 137', ' 432', ' 165', '2'], ['3753', '89', '395', ' 137', ' 434', ' 167', '2'], ['3754', '89', '396', ' 138', ' 435', ' 168', '2'], ['3755', '89', '397', ' 140', ' 436', ' 168', '2'], ['3756', '89', '398', ' 140', ' 437', ' 169', '2'], ['3757', '89', '398', ' 141', ' 439', ' 171', '2'], ['3758', '89', '399', ' 142', ' 439', ' 172', '2'], ['3759', '89', '398', ' 142', ' 439', ' 173', '2'], ['3760', '89', '399', ' 142', ' 440', ' 173', '2'], ['3761', '89', '399', ' 143', ' 439', ' 173', '2'], ['3762', '89', '400', ' 143', ' 439', ' 173', '2'], ['3763', '89', '401', ' 144', ' 439', ' 174', '2'], ['3764', '89', '401', ' 145', ' 441', ' 176', '2'], ['3765', '89', '401', ' 146', ' 440', ' 177', '2'], ['3766', '89', '401', ' 147', ' 441', ' 179', '2'], ['3767', '89', '401', ' 148', ' 441', ' 179', '2'], ['3768', '89', '401', ' 148', ' 442', ' 180', '2'], ['3769', '89', '402', ' 148', ' 444', ' 182', '2'], ['3770', '89', '403', ' 149', ' 445', ' 183', '2'], ['3771', '89', '404', ' 149', ' 446', ' 183', '2'], ['3772', '89', '404', ' 149', ' 447', ' 185', '2'], ['3773', '89', '406', ' 151', ' 447', ' 185', '2'], ['3774', '89', '408', ' 153', ' 448', ' 186', '2'], ['3775', '89', '408', ' 154', ' 449', ' 188', '2'], ['3776', '89', '409', ' 155', ' 450', ' 189', '2'], ['3777', '89', '409', ' 156', ' 451', ' 191', '2'], ['3778', '89', '411', ' 158', ' 453', ' 192', '2'], ['3779', '89', '412', ' 158', ' 455', ' 194', '2'], ['3780', '89', '413', ' 160', ' 456', ' 196', '2'], ['3781', '89', '413', ' 161', ' 457', ' 198', '2'], ['3782', '89', '414', ' 161', ' 458', ' 199', '2'], ['3783', '89', '413', ' 162', ' 460', ' 202', '2'], ['3784', '89', '414', ' 163', ' 461', ' 203', '2'], ['3785', '89', '415', ' 163', ' 463', ' 205', '2'], ['3786', '89', '417', ' 165', ' 464', ' 205', '2'], ['3787', '89', '418', ' 165', ' 466', ' 208', '2'], ['3788', '89', '419', ' 167', ' 467', ' 210', '2'], ['3789', '89', '421', ' 169', ' 469', ' 212', '2'], ['3790', '89', '421', ' 171', ' 470', ' 214', '2'], ['3791', '89', '422', ' 173', ' 470', ' 216', '2'], ['3792', '89', '423', ' 174', ' 472', ' 218', '2'], ['3793', '89', '423', ' 175', ' 474', ' 221', '2'], ['3794', '89', '424', ' 177', ' 475', ' 223', '2'], ['3795', '89', '426', ' 179', ' 477', ' 226', '2'], ['3796', '89', '427', ' 179', ' 480', ' 228', '2'], ['3797', '89', '428', ' 181', ' 482', ' 231', '2'], ['3798', '89', '429', ' 182', ' 484', ' 233', '2'], ['3799', '89', '432', ' 185', ' 486', ' 236', '2'], ['3800', '89', '433', ' 188', ' 487', ' 238', '2'], ['3801', '89', '434', ' 189', ' 490', ' 242', '2'], ['3802', '89', '435', ' 190', ' 494', ' 245', '2'], ['3803', '89', '436', ' 193', ' 495', ' 248', '2'], ['3804', '89', '436', ' 193', ' 497', ' 251', '2'], ['3805', '89', '437', ' 195', ' 500', ' 254', '2'], ['3806', '89', '437', ' 197', ' 503', ' 258', '2'], ['3807', '89', '439', ' 200', ' 504', ' 261', '2'], ['3808', '89', '442', ' 202', ' 508', ' 264', '2'], ['3809', '89', '442', ' 203', ' 510', ' 267', '2'], ['3810', '89', '444', ' 206', ' 513', ' 272', '2'], ['3811', '89', '445', ' 209', ' 515', ' 275', '2'], ['3812', '89', '447', ' 213', ' 517', ' 280', '2'], ['3813', '89', '448', ' 216', ' 519', ' 284', '2'], ['3814', '89', '449', ' 218', ' 522', ' 287', '2'], ['3815', '89', '451', ' 221', ' 527', ' 294', '2'], ['3816', '89', '453', ' 224', ' 530', ' 298', '2'], ['3817', '89', '455', ' 227', ' 533', ' 301', '2'], ['3818', '89', '457', ' 230', ' 536', ' 306', '2'], ['3819', '89', '459', ' 234', ' 540', ' 312', '2'], ['3820', '89', '461', ' 238', ' 545', ' 318', '2'], ['3821', '89', '463', ' 241', ' 549', ' 323', '2'], ['3822', '89', '465', ' 245', ' 554', ' 330', '2'], ['3823', '89', '468', ' 249', ' 560', ' 337', '2'], ['3824', '89', '470', ' 252', ' 564', ' 343', '2'], ['3825', '89', '473', ' 257', ' 567', ' 348', '2'], ['3826', '89', '476', ' 262', ' 573', ' 356', '2'], ['3827', '89', '478', ' 267', ' 578', ' 363', '2'], ['3828', '89', '480', ' 271', ' 584', ' 372', '2'], ['3829', '89', '482', ' 275', ' 591', ' 381', '2'], ['3830', '89', '486', ' 280', ' 596', ' 388', '2'], ['3831', '89', '489', ' 287', ' 603', ' 398', '2'], ['3832', '89', '492', ' 293', ' 610', ' 408', '2'], ['3833', '89', '497', ' 299', ' 614', ' 413', '2'], ['3834', '89', '504', ' 305', ' 619', ' 416', '2'], ['3835', '89', '512', ' 312', ' 624', ' 417', '2'], ['3836', '89', '520', ' 317', ' 628', ' 416', '2'], ['3837', '89', '527', ' 324', ' 628', ' 413', '2'], ['3838', '89', '533', ' 333', ' 631', ' 416', '2']]}, {'98': [['4111', '98', '358', ' 106', ' 380', ' 121', '2'], ['4112', '98', '358', ' 107', ' 380', ' 122', '2'], ['4113', '98', '358', ' 107', ' 379', ' 122', '2'], ['4114', '98', '359', ' 108', ' 379', ' 122', '2'], ['4115', '98', '358', ' 108', ' 380', ' 122', '2'], ['4116', '98', '358', ' 107', ' 381', ' 123', '2'], ['4117', '98', '356', ' 105', ' 382', ' 123', '2'], ['4118', '98', '356', ' 105', ' 383', ' 123', '2'], ['4119', '98', '357', ' 106', ' 383', ' 123', '2'], ['4120', '98', '356', ' 106', ' 384', ' 124', '2'], ['4121', '98', '357', ' 105', ' 384', ' 125', '2'], ['4122', '98', '357', ' 105', ' 384', ' 125', '2'], ['4123', '98', '357', ' 105', ' 384', ' 125', '2'], ['4124', '98', '357', ' 105', ' 385', ' 125', '2'], ['4125', '98', '357', ' 105', ' 385', ' 126', '2'], ['4126', '98', '357', ' 105', ' 386', ' 126', '2'], ['4127', '98', '357', ' 105', ' 386', ' 126', '2'], ['4128', '98', '357', ' 105', ' 387', ' 127', '2'], ['4129', '98', '357', ' 105', ' 387', ' 127', '2'], ['4130', '98', '357', ' 104', ' 387', ' 127', '2'], ['4131', '98', '358', ' 105', ' 387', ' 127', '2'], ['4132', '98', '359', ' 106', ' 386', ' 127', '2'], ['4133', '98', '358', ' 106', ' 386', ' 127', '2'], ['4134', '98', '358', ' 105', ' 387', ' 128', '2'], ['4135', '98', '357', ' 104', ' 388', ' 129', '2'], ['4136', '98', '357', ' 103', ' 388', ' 129', '2'], ['4137', '98', '357', ' 103', ' 388', ' 129', '2'], ['4138', '98', '358', ' 103', ' 389', ' 129', '2'], ['4139', '98', '357', ' 102', ' 389', ' 130', '2'], ['4140', '98', '358', ' 102', ' 389', ' 130', '2'], ['4141', '98', '357', ' 101', ' 389', ' 130', '2'], ['4142', '98', '358', ' 101', ' 389', ' 131', '2'], ['4143', '98', '358', ' 102', ' 389', ' 131', '2'], ['4144', '98', '360', ' 105', ' 388', ' 132', '2'], ['4145', '98', '361', ' 104', ' 389', ' 132', '2'], ['4146', '98', '361', ' 104', ' 389', ' 132', '2'], ['4147', '98', '361', ' 103', ' 390', ' 133', '2'], ['4148', '98', '362', ' 104', ' 389', ' 133', '2'], ['4149', '98', '363', ' 105', ' 389', ' 133', '2'], ['4150', '98', '363', ' 105', ' 389', ' 133', '2'], ['4151', '98', '364', ' 108', ' 388', ' 134', '2'], ['4152', '98', '364', ' 110', ' 388', ' 134', '2'], ['4153', '98', '365', ' 111', ' 388', ' 134', '2'], ['4154', '98', '365', ' 112', ' 388', ' 135', '2'], ['4155', '98', '366', ' 114', ' 389', ' 136', '2'], ['4156', '98', '366', ' 115', ' 389', ' 137', '2'], ['4157', '98', '365', ' 115', ' 390', ' 138', '2'], ['4158', '98', '365', ' 116', ' 390', ' 138', '2'], ['4159', '98', '366', ' 118', ' 390', ' 139', '2'], ['4160', '98', '367', ' 119', ' 391', ' 140', '2'], ['4161', '98', '366', ' 118', ' 391', ' 140', '2'], ['4162', '98', '366', ' 119', ' 391', ' 141', '2'], ['4163', '98', '367', ' 119', ' 392', ' 141', '2'], ['4164', '98', '367', ' 120', ' 392', ' 141', '2'], ['4166', '98', '367', ' 120', ' 394', ' 142', '2'], ['4167', '98', '366', ' 119', ' 395', ' 143', '2'], ['4168', '98', '366', ' 119', ' 395', ' 144', '2'], ['4169', '98', '366', ' 119', ' 395', ' 144', '2'], ['4170', '98', '366', ' 120', ' 396', ' 145', '2'], ['4171', '98', '366', ' 120', ' 396', ' 145', '2'], ['4172', '98', '367', ' 122', ' 396', ' 146', '2'], ['4173', '98', '367', ' 122', ' 397', ' 147', '2'], ['4174', '98', '367', ' 122', ' 397', ' 147', '2'], ['4175', '98', '367', ' 122', ' 397', ' 147', '2'], ['4176', '98', '368', ' 123', ' 397', ' 148', '2'], ['4177', '98', '368', ' 124', ' 398', ' 148', '2'], ['4178', '98', '368', ' 125', ' 397', ' 149', '2'], ['4179', '98', '368', ' 126', ' 398', ' 150', '2'], ['4180', '98', '367', ' 126', ' 399', ' 151', '2'], ['4181', '98', '368', ' 126', ' 399', ' 152', '2'], ['4182', '98', '368', ' 127', ' 400', ' 152', '2'], ['4183', '98', '369', ' 127', ' 400', ' 153', '2'], ['4184', '98', '369', ' 128', ' 400', ' 153', '2'], ['4185', '98', '370', ' 128', ' 401', ' 154', '2'], ['4186', '98', '369', ' 128', ' 402', ' 154', '2'], ['4187', '98', '369', ' 128', ' 403', ' 155', '2'], ['4188', '98', '369', ' 128', ' 403', ' 156', '2'], ['4189', '98', '370', ' 128', ' 404', ' 156', '2'], ['4190', '98', '370', ' 129', ' 404', ' 157', '2'], ['4191', '98', '370', ' 129', ' 405', ' 158', '2'], ['4192', '98', '369', ' 130', ' 406', ' 160', '2'], ['4193', '98', '370', ' 130', ' 407', ' 161', '2'], ['4194', '98', '371', ' 131', ' 407', ' 162', '2'], ['4195', '98', '371', ' 131', ' 408', ' 162', '2'], ['4196', '98', '372', ' 132', ' 409', ' 164', '2'], ['4197', '98', '372', ' 132', ' 410', ' 165', '2'], ['4198', '98', '372', ' 134', ' 411', ' 166', '2'], ['4199', '98', '372', ' 134', ' 411', ' 167', '2'], ['4200', '98', '372', ' 134', ' 411', ' 168', '2'], ['4201', '98', '371', ' 135', ' 412', ' 170', '2'], ['4202', '98', '372', ' 135', ' 412', ' 170', '2'], ['4203', '98', '373', ' 136', ' 413', ' 171', '2'], ['4204', '98', '373', ' 136', ' 413', ' 172', '2'], ['4205', '98', '373', ' 136', ' 414', ' 173', '2'], ['4206', '98', '374', ' 138', ' 415', ' 174', '2'], ['4207', '98', '375', ' 140', ' 415', ' 175', '2'], ['4208', '98', '376', ' 141', ' 416', ' 177', '2'], ['4209', '98', '376', ' 141', ' 417', ' 178', '2'], ['4210', '98', '375', ' 142', ' 418', ' 179', '2'], ['4211', '98', '377', ' 144', ' 417', ' 180', '2'], ['4212', '98', '377', ' 145', ' 418', ' 182', '2'], ['4213', '98', '378', ' 147', ' 418', ' 183', '2'], ['4214', '98', '378', ' 148', ' 419', ' 184', '2'], ['4215', '98', '378', ' 148', ' 421', ' 185', '2'], ['4216', '98', '379', ' 149', ' 422', ' 186', '2'], ['4217', '98', '379', ' 151', ' 422', ' 188', '2'], ['4218', '98', '379', ' 151', ' 424', ' 190', '2'], ['4219', '98', '380', ' 151', ' 425', ' 191', '2'], ['4220', '98', '382', ' 153', ' 426', ' 192', '2'], ['4221', '98', '382', ' 154', ' 428', ' 194', '2'], ['4222', '98', '381', ' 154', ' 430', ' 197', '2'], ['4223', '98', '382', ' 155', ' 431', ' 198', '2'], ['4224', '98', '382', ' 156', ' 432', ' 201', '2'], ['4225', '98', '382', ' 156', ' 433', ' 202', '2'], ['4226', '98', '383', ' 158', ' 434', ' 204', '2'], ['4227', '98', '385', ' 161', ' 435', ' 206', '2'], ['4228', '98', '385', ' 161', ' 436', ' 207', '2'], ['4229', '98', '386', ' 162', ' 438', ' 209', '2'], ['4230', '98', '387', ' 162', ' 440', ' 211', '2'], ['4231', '98', '388', ' 164', ' 441', ' 213', '2'], ['4232', '98', '387', ' 165', ' 442', ' 216', '2'], ['4233', '98', '387', ' 166', ' 443', ' 218', '2'], ['4234', '98', '388', ' 167', ' 445', ' 221', '2'], ['4235', '98', '389', ' 168', ' 447', ' 223', '2'], ['4236', '98', '390', ' 170', ' 449', ' 226', '2'], ['4237', '98', '390', ' 171', ' 449', ' 227', '2'], ['4238', '98', '393', ' 173', ' 451', ' 229', '2'], ['4239', '98', '394', ' 175', ' 454', ' 232', '2'], ['4240', '98', '394', ' 176', ' 457', ' 236', '2'], ['4241', '98', '394', ' 177', ' 458', ' 238', '2'], ['4242', '98', '395', ' 179', ' 460', ' 242', '2'], ['4243', '98', '396', ' 182', ' 463', ' 246', '2'], ['4244', '98', '396', ' 183', ' 465', ' 250', '2'], ['4245', '98', '399', ' 186', ' 467', ' 253', '2'], ['4246', '98', '399', ' 188', ' 469', ' 255', '2'], ['4247', '98', '401', ' 190', ' 472', ' 260', '2'], ['4248', '98', '401', ' 192', ' 475', ' 264', '2'], ['4249', '98', '403', ' 195', ' 478', ' 268', '2'], ['4250', '98', '405', ' 198', ' 480', ' 271', '2'], ['4251', '98', '405', ' 200', ' 483', ' 276', '2'], ['4252', '98', '405', ' 203', ' 486', ' 281', '2'], ['4253', '98', '406', ' 206', ' 489', ' 286', '2'], ['4254', '98', '408', ' 208', ' 493', ' 290', '2'], ['4255', '98', '409', ' 211', ' 496', ' 296', '2'], ['4256', '98', '411', ' 214', ' 500', ' 300', '2'], ['4257', '98', '412', ' 217', ' 503', ' 306', '2'], ['4258', '98', '414', ' 221', ' 508', ' 311', '2'], ['4259', '98', '416', ' 224', ' 514', ' 320', '2'], ['4260', '98', '417', ' 228', ' 517', ' 326', '2'], ['4261', '98', '419', ' 232', ' 521', ' 332', '2'], ['4262', '98', '422', ' 236', ' 525', ' 337', '2'], ['4263', '98', '424', ' 241', ' 532', ' 346', '2'], ['4264', '98', '426', ' 244', ' 538', ' 353', '2'], ['4265', '98', '429', ' 249', ' 543', ' 361', '2'], ['4266', '98', '431', ' 254', ' 551', ' 372', '2'], ['4267', '98', '433', ' 259', ' 558', ' 383', '2'], ['4268', '98', '434', ' 265', ' 569', ' 399', '2'], ['4269', '98', '437', ' 270', ' 577', ' 408', '2'], ['4270', '98', '442', ' 276', ' 581', ' 413', '2'], ['4271', '98', '448', ' 282', ' 586', ' 417', '2'], ['4272', '98', '456', ' 290', ' 590', ' 420', '2'], ['4273', '98', '468', ' 297', ' 597', ' 419', '2']]}, {'99': [['4215', '99', '363', ' 106', ' 383', ' 119', '2'], ['4216', '99', '364', ' 105', ' 384', ' 118', '2'], ['4217', '99', '364', ' 105', ' 384', ' 118', '2'], ['4218', '99', '363', ' 106', ' 384', ' 119', '2'], ['4219', '99', '363', ' 106', ' 384', ' 120', '2'], ['4220', '99', '363', ' 106', ' 385', ' 120', '2'], ['4221', '99', '363', ' 106', ' 386', ' 120', '2'], ['4222', '99', '363', ' 106', ' 386', ' 121', '2'], ['4223', '99', '364', ' 106', ' 386', ' 121', '2'], ['4224', '99', '364', ' 106', ' 386', ' 121', '2'], ['4225', '99', '363', ' 106', ' 386', ' 121', '2'], ['4226', '99', '363', ' 107', ' 386', ' 122', '2'], ['4227', '99', '363', ' 107', ' 387', ' 123', '2'], ['4228', '99', '363', ' 107', ' 386', ' 122', '2'], ['4229', '99', '363', ' 107', ' 386', ' 122', '2'], ['4230', '99', '362', ' 107', ' 386', ' 123', '2'], ['4231', '99', '362', ' 108', ' 387', ' 124', '2'], ['4232', '99', '362', ' 108', ' 388', ' 125', '2'], ['4233', '99', '362', ' 108', ' 388', ' 125', '2'], ['4234', '99', '362', ' 108', ' 387', ' 125', '2'], ['4235', '99', '362', ' 109', ' 387', ' 126', '2'], ['4236', '99', '362', ' 109', ' 387', ' 126', '2'], ['4237', '99', '362', ' 108', ' 388', ' 126', '2'], ['4238', '99', '362', ' 108', ' 388', ' 126', '2'], ['4239', '99', '363', ' 109', ' 389', ' 127', '2'], ['4240', '99', '363', ' 109', ' 389', ' 127', '2'], ['4241', '99', '364', ' 109', ' 389', ' 128', '2'], ['4242', '99', '364', ' 110', ' 389', ' 128', '2'], ['4243', '99', '364', ' 110', ' 389', ' 128', '2'], ['4244', '99', '363', ' 110', ' 389', ' 129', '2'], ['4245', '99', '364', ' 110', ' 390', ' 129', '2'], ['4246', '99', '364', ' 111', ' 389', ' 130', '2'], ['4247', '99', '364', ' 112', ' 389', ' 130', '2'], ['4248', '99', '365', ' 113', ' 389', ' 131', '2'], ['4249', '99', '364', ' 114', ' 389', ' 131', '2'], ['4250', '99', '366', ' 115', ' 389', ' 132', '2'], ['4251', '99', '366', ' 116', ' 390', ' 132', '2'], ['4252', '99', '366', ' 116', ' 390', ' 133', '2'], ['4253', '99', '367', ' 117', ' 391', ' 134', '2'], ['4254', '99', '366', ' 116', ' 392', ' 134', '2'], ['4255', '99', '366', ' 116', ' 393', ' 134', '2'], ['4256', '99', '366', ' 117', ' 393', ' 135', '2'], ['4257', '99', '367', ' 117', ' 393', ' 135', '2'], ['4258', '99', '366', ' 116', ' 394', ' 135', '2'], ['4259', '99', '365', ' 116', ' 395', ' 137', '2'], ['4260', '99', '365', ' 116', ' 396', ' 138', '2'], ['4261', '99', '365', ' 116', ' 395', ' 139', '2'], ['4262', '99', '366', ' 117', ' 396', ' 139', '2'], ['4263', '99', '366', ' 116', ' 398', ' 140', '2'], ['4264', '99', '366', ' 116', ' 399', ' 141', '2'], ['4265', '99', '366', ' 117', ' 399', ' 142', '2'], ['4266', '99', '367', ' 118', ' 398', ' 142', '2'], ['4267', '99', '367', ' 118', ' 398', ' 142', '2'], ['4268', '99', '367', ' 119', ' 398', ' 144', '2'], ['4269', '99', '368', ' 120', ' 398', ' 144', '2'], ['4270', '99', '368', ' 121', ' 397', ' 145', '2'], ['4271', '99', '369', ' 123', ' 397', ' 146', '2'], ['4272', '99', '369', ' 124', ' 398', ' 146', '2'], ['4273', '99', '370', ' 125', ' 398', ' 147', '2'], ['4274', '99', '371', ' 125', ' 399', ' 147', '2'], ['4275', '99', '371', ' 126', ' 399', ' 148', '2'], ['4276', '99', '370', ' 126', ' 400', ' 149', '2'], ['4277', '99', '369', ' 126', ' 401', ' 150', '2'], ['4278', '99', '368', ' 126', ' 401', ' 151', '2'], ['4279', '99', '369', ' 127', ' 401', ' 151', '2'], ['4280', '99', '369', ' 128', ' 401', ' 152', '2'], ['4281', '99', '369', ' 128', ' 402', ' 153', '2'], ['4282', '99', '369', ' 129', ' 402', ' 154', '2'], ['4283', '99', '368', ' 129', ' 402', ' 155', '2'], ['4284', '99', '368', ' 129', ' 403', ' 156', '2'], ['4285', '99', '368', ' 130', ' 403', ' 157', '2'], ['4286', '99', '368', ' 131', ' 404', ' 158', '2'], ['4287', '99', '368', ' 132', ' 403', ' 159', '2'], ['4288', '99', '369', ' 134', ' 404', ' 161', '2'], ['4289', '99', '369', ' 135', ' 405', ' 163', '2'], ['4290', '99', '369', ' 135', ' 406', ' 164', '2'], ['4291', '99', '370', ' 137', ' 407', ' 166', '2'], ['4292', '99', '370', ' 138', ' 407', ' 167', '2'], ['4293', '99', '371', ' 139', ' 408', ' 168', '2'], ['4294', '99', '371', ' 140', ' 408', ' 169', '2'], ['4295', '99', '370', ' 140', ' 410', ' 171', '2'], ['4296', '99', '371', ' 140', ' 411', ' 172', '2'], ['4297', '99', '371', ' 142', ' 411', ' 173', '2'], ['4298', '99', '371', ' 142', ' 412', ' 174', '2'], ['4299', '99', '371', ' 143', ' 413', ' 177', '2'], ['4300', '99', '371', ' 144', ' 413', ' 178', '2'], ['4301', '99', '372', ' 147', ' 413', ' 180', '2'], ['4302', '99', '373', ' 148', ' 415', ' 181', '2'], ['4303', '99', '373', ' 149', ' 416', ' 184', '2'], ['4304', '99', '375', ' 152', ' 417', ' 186', '2'], ['4305', '99', '375', ' 153', ' 417', ' 187', '2'], ['4306', '99', '377', ' 156', ' 419', ' 190', '2'], ['4307', '99', '379', ' 157', ' 421', ' 191', '2'], ['4308', '99', '380', ' 157', ' 423', ' 193', '2'], ['4309', '99', '379', ' 158', ' 425', ' 195', '2'], ['4310', '99', '380', ' 159', ' 427', ' 198', '2'], ['4311', '99', '380', ' 161', ' 428', ' 200', '2'], ['4312', '99', '381', ' 163', ' 430', ' 203', '2'], ['4313', '99', '382', ' 165', ' 432', ' 205', '2'], ['4314', '99', '384', ' 167', ' 433', ' 207', '2'], ['4315', '99', '386', ' 168', ' 436', ' 209', '2'], ['4316', '99', '388', ' 170', ' 440', ' 212', '2'], ['4317', '99', '387', ' 171', ' 441', ' 216', '2'], ['4318', '99', '388', ' 173', ' 444', ' 219', '2'], ['4319', '99', '389', ' 175', ' 447', ' 223', '2'], ['4320', '99', '390', ' 176', ' 449', ' 226', '2'], ['4321', '99', '392', ' 178', ' 453', ' 229', '2'], ['4322', '99', '394', ' 180', ' 456', ' 232', '2'], ['4323', '99', '396', ' 183', ' 458', ' 235', '2'], ['4324', '99', '398', ' 185', ' 462', ' 240', '2'], ['4325', '99', '400', ' 189', ' 466', ' 245', '2'], ['4326', '99', '402', ' 193', ' 468', ' 249', '2'], ['4327', '99', '405', ' 196', ' 472', ' 253', '2'], ['4328', '99', '407', ' 199', ' 477', ' 258', '2'], ['4329', '99', '408', ' 200', ' 482', ' 262', '2'], ['4330', '99', '409', ' 203', ' 488', ' 269', '2'], ['4331', '99', '412', ' 207', ' 492', ' 274', '2'], ['4332', '99', '416', ' 211', ' 497', ' 279', '2'], ['4333', '99', '418', ' 215', ' 503', ' 287', '2'], ['4334', '99', '421', ' 219', ' 509', ' 293', '2'], ['4335', '99', '424', ' 223', ' 515', ' 300', '2'], ['4336', '99', '426', ' 226', ' 521', ' 307', '2'], ['4337', '99', '432', ' 231', ' 528', ' 314', '2'], ['4338', '99', '436', ' 236', ' 536', ' 322', '2'], ['4339', '99', '439', ' 242', ' 543', ' 330', '2'], ['4340', '99', '444', ' 248', ' 552', ' 340', '2'], ['4341', '99', '450', ' 254', ' 560', ' 349', '2'], ['4342', '99', '455', ' 261', ' 571', ' 360', '2'], ['4343', '99', '461', ' 267', ' 582', ' 371', '2'], ['4344', '99', '466', ' 274', ' 593', ' 383', '2'], ['4345', '99', '471', ' 282', ' 605', ' 397', '2'], ['4346', '99', '478', ' 290', ' 617', ' 410', '2'], ['4347', '99', '490', ' 298', ' 627', ' 416', '2'], ['4348', '99', '504', ' 307', ' 640', ' 420', '2'], ['4349', '99', '518', ' 317', ' 644', ' 419', '2'], ['4350', '99', '531', ' 327', ' 647', ' 418', '2'], ['4351', '99', '548', ' 340', ' 655', ' 417', '2']]}, {'105': [['4411', '105', '345', ' 108', ' 374', ' 129', '2'], ['4415', '105', '347', ' 108', ' 375', ' 130', '2'], ['4416', '105', '348', ' 109', ' 375', ' 130', '2'], ['4417', '105', '349', ' 110', ' 375', ' 131', '2'], ['4418', '105', '348', ' 111', ' 374', ' 131', '2'], ['4419', '105', '349', ' 111', ' 374', ' 132', '2'], ['4420', '105', '349', ' 111', ' 374', ' 132', '2'], ['4421', '105', '349', ' 111', ' 374', ' 132', '2'], ['4422', '105', '349', ' 110', ' 375', ' 131', '2'], ['4423', '105', '349', ' 109', ' 375', ' 132', '2'], ['4424', '105', '349', ' 108', ' 376', ' 132', '2'], ['4425', '105', '349', ' 109', ' 377', ' 133', '2'], ['4426', '105', '351', ' 111', ' 377', ' 133', '2'], ['4427', '105', '352', ' 111', ' 377', ' 134', '2'], ['4428', '105', '351', ' 112', ' 377', ' 134', '2'], ['4429', '105', '352', ' 112', ' 377', ' 134', '2'], ['4430', '105', '352', ' 113', ' 377', ' 134', '2'], ['4431', '105', '352', ' 113', ' 377', ' 135', '2'], ['4432', '105', '353', ' 114', ' 377', ' 135', '2'], ['4433', '105', '353', ' 114', ' 378', ' 136', '2'], ['4434', '105', '353', ' 114', ' 379', ' 136', '2'], ['4435', '105', '352', ' 113', ' 380', ' 137', '2'], ['4436', '105', '352', ' 113', ' 381', ' 138', '2'], ['4437', '105', '352', ' 113', ' 381', ' 138', '2'], ['4438', '105', '351', ' 112', ' 382', ' 139', '2'], ['4439', '105', '351', ' 112', ' 382', ' 139', '2'], ['4440', '105', '352', ' 112', ' 382', ' 139', '2'], ['4441', '105', '353', ' 114', ' 382', ' 140', '2'], ['4442', '105', '354', ' 114', ' 383', ' 140', '2'], ['4443', '105', '355', ' 114', ' 383', ' 140', '2'], ['4444', '105', '354', ' 114', ' 384', ' 140', '2'], ['4445', '105', '354', ' 114', ' 384', ' 141', '2'], ['4446', '105', '355', ' 115', ' 384', ' 141', '2'], ['4447', '105', '355', ' 115', ' 384', ' 141', '2'], ['4448', '105', '356', ' 116', ' 384', ' 141', '2'], ['4449', '105', '356', ' 117', ' 384', ' 141', '2'], ['4450', '105', '356', ' 117', ' 385', ' 142', '2'], ['4451', '105', '356', ' 117', ' 385', ' 143', '2'], ['4452', '105', '357', ' 117', ' 385', ' 143', '2'], ['4453', '105', '357', ' 118', ' 385', ' 143', '2'], ['4454', '105', '357', ' 118', ' 385', ' 144', '2'], ['4455', '105', '358', ' 119', ' 385', ' 144', '2'], ['4456', '105', '358', ' 119', ' 386', ' 145', '2'], ['4457', '105', '357', ' 119', ' 386', ' 145', '2'], ['4458', '105', '358', ' 119', ' 386', ' 146', '2'], ['4459', '105', '358', ' 120', ' 387', ' 146', '2'], ['4460', '105', '359', ' 121', ' 387', ' 147', '2'], ['4461', '105', '358', ' 121', ' 387', ' 147', '2'], ['4462', '105', '359', ' 121', ' 387', ' 147', '2'], ['4463', '105', '360', ' 122', ' 388', ' 147', '2'], ['4464', '105', '361', ' 123', ' 389', ' 147', '2'], ['4465', '105', '361', ' 123', ' 389', ' 148', '2'], ['4466', '105', '361', ' 124', ' 390', ' 149', '2'], ['4467', '105', '361', ' 124', ' 391', ' 150', '2'], ['4468', '105', '360', ' 125', ' 391', ' 151', '2'], ['4469', '105', '361', ' 126', ' 392', ' 152', '2'], ['4470', '105', '362', ' 126', ' 394', ' 152', '2'], ['4471', '105', '361', ' 126', ' 394', ' 152', '2'], ['4472', '105', '362', ' 126', ' 395', ' 153', '2'], ['4473', '105', '363', ' 127', ' 395', ' 153', '2'], ['4474', '105', '363', ' 128', ' 395', ' 153', '2'], ['4475', '105', '364', ' 128', ' 396', ' 154', '2'], ['4476', '105', '363', ' 127', ' 397', ' 154', '2'], ['4477', '105', '364', ' 128', ' 397', ' 155', '2'], ['4478', '105', '364', ' 129', ' 398', ' 156', '2'], ['4479', '105', '364', ' 129', ' 398', ' 157', '2'], ['4480', '105', '364', ' 128', ' 400', ' 157', '2'], ['4481', '105', '364', ' 128', ' 400', ' 158', '2'], ['4482', '105', '365', ' 129', ' 400', ' 158', '2'], ['4483', '105', '365', ' 129', ' 400', ' 158', '2'], ['4484', '105', '365', ' 129', ' 401', ' 159', '2'], ['4485', '105', '365', ' 130', ' 401', ' 160', '2'], ['4486', '105', '364', ' 130', ' 402', ' 161', '2'], ['4487', '105', '365', ' 130', ' 403', ' 163', '2'], ['4488', '105', '366', ' 131', ' 404', ' 164', '2'], ['4489', '105', '367', ' 132', ' 405', ' 165', '2'], ['4490', '105', '367', ' 132', ' 405', ' 165', '2'], ['4491', '105', '368', ' 132', ' 407', ' 166', '2'], ['4492', '105', '368', ' 133', ' 406', ' 167', '2'], ['4493', '105', '368', ' 133', ' 407', ' 167', '2'], ['4494', '105', '369', ' 134', ' 408', ' 169', '2'], ['4495', '105', '369', ' 135', ' 408', ' 169', '2'], ['4496', '105', '370', ' 135', ' 409', ' 170', '2'], ['4497', '105', '370', ' 136', ' 410', ' 171', '2'], ['4498', '105', '370', ' 136', ' 410', ' 171', '2'], ['4499', '105', '371', ' 136', ' 411', ' 171', '2'], ['4500', '105', '371', ' 138', ' 411', ' 173', '2'], ['4501', '105', '371', ' 139', ' 411', ' 174', '2'], ['4502', '105', '372', ' 140', ' 412', ' 175', '2'], ['4503', '105', '373', ' 140', ' 414', ' 176', '2'], ['4504', '105', '373', ' 140', ' 414', ' 177', '2'], ['4505', '105', '373', ' 141', ' 415', ' 178', '2'], ['4506', '105', '374', ' 142', ' 416', ' 179', '2'], ['4507', '105', '375', ' 142', ' 416', ' 180', '2'], ['4508', '105', '375', ' 144', ' 417', ' 181', '2'], ['4509', '105', '376', ' 145', ' 417', ' 182', '2'], ['4510', '105', '376', ' 145', ' 419', ' 184', '2'], ['4511', '105', '377', ' 147', ' 419', ' 185', '2'], ['4512', '105', '378', ' 147', ' 421', ' 186', '2'], ['4513', '105', '378', ' 147', ' 422', ' 187', '2'], ['4514', '105', '379', ' 148', ' 423', ' 188', '2'], ['4515', '105', '379', ' 149', ' 423', ' 189', '2'], ['4516', '105', '380', ' 150', ' 424', ' 189', '2'], ['4517', '105', '381', ' 150', ' 425', ' 190', '2'], ['4518', '105', '381', ' 151', ' 427', ' 193', '2'], ['4519', '105', '381', ' 151', ' 429', ' 195', '2'], ['4520', '105', '381', ' 152', ' 431', ' 197', '2'], ['4521', '105', '382', ' 154', ' 431', ' 199', '2'], ['4522', '105', '383', ' 154', ' 433', ' 200', '2'], ['4523', '105', '385', ' 156', ' 434', ' 202', '2'], ['4524', '105', '385', ' 157', ' 435', ' 204', '2'], ['4525', '105', '385', ' 157', ' 436', ' 205', '2'], ['4526', '105', '386', ' 158', ' 438', ' 207', '2'], ['4527', '105', '388', ' 160', ' 439', ' 208', '2'], ['4528', '105', '390', ' 162', ' 441', ' 209', '2'], ['4529', '105', '390', ' 162', ' 443', ' 211', '2'], ['4530', '105', '389', ' 163', ' 444', ' 213', '2'], ['4531', '105', '389', ' 162', ' 446', ' 215', '2'], ['4532', '105', '389', ' 163', ' 447', ' 216', '2'], ['4533', '105', '390', ' 165', ' 448', ' 219', '2'], ['4534', '105', '391', ' 168', ' 450', ' 223', '2'], ['4535', '105', '392', ' 169', ' 452', ' 225', '2'], ['4536', '105', '393', ' 171', ' 454', ' 227', '2'], ['4537', '105', '394', ' 173', ' 454', ' 228', '2'], ['4538', '105', '396', ' 175', ' 456', ' 230', '2'], ['4539', '105', '396', ' 175', ' 459', ' 233', '2'], ['4540', '105', '398', ' 177', ' 459', ' 233', '2'], ['4541', '105', '400', ' 179', ' 462', ' 236', '2'], ['4542', '105', '402', ' 181', ' 466', ' 240', '2'], ['4543', '105', '402', ' 183', ' 469', ' 244', '2'], ['4544', '105', '401', ' 184', ' 471', ' 248', '2'], ['4545', '105', '403', ' 186', ' 474', ' 251', '2'], ['4546', '105', '405', ' 188', ' 476', ' 254', '2'], ['4547', '105', '407', ' 192', ' 477', ' 255', '2'], ['4548', '105', '408', ' 193', ' 481', ' 260', '2'], ['4549', '105', '409', ' 195', ' 484', ' 262', '2'], ['4550', '105', '411', ' 196', ' 488', ' 265', '2'], ['4551', '105', '414', ' 200', ' 491', ' 269', '2'], ['4552', '105', '415', ' 201', ' 495', ' 274', '2'], ['4553', '105', '416', ' 203', ' 499', ' 278', '2'], ['4554', '105', '417', ' 205', ' 503', ' 282', '2'], ['4555', '105', '418', ' 208', ' 505', ' 286', '2'], ['4556', '105', '419', ' 209', ' 510', ' 292', '2'], ['4557', '105', '421', ' 212', ' 513', ' 296', '2'], ['4558', '105', '423', ' 214', ' 518', ' 299', '2'], ['4559', '105', '426', ' 216', ' 522', ' 303', '2'], ['4560', '105', '427', ' 219', ' 527', ' 310', '2'], ['4561', '105', '430', ' 223', ' 532', ' 316', '2'], ['4562', '105', '432', ' 226', ' 536', ' 322', '2'], ['4563', '105', '434', ' 229', ' 541', ' 328', '2'], ['4564', '105', '436', ' 232', ' 547', ' 334', '2'], ['4565', '105', '440', ' 236', ' 551', ' 339', '2'], ['4566', '105', '442', ' 241', ' 557', ' 347', '2'], ['4567', '105', '445', ' 244', ' 564', ' 354', '2'], ['4569', '105', '451', ' 252', ' 575', ' 366', '2'], ['4570', '105', '455', ' 258', ' 584', ' 376', '2'], ['4571', '105', '460', ' 263', ' 591', ' 384', '2'], ['4572', '105', '462', ' 268', ' 601', ' 397', '2'], ['4573', '105', '466', ' 274', ' 610', ' 408', '2'], ['4574', '105', '472', ' 278', ' 617', ' 414', '2'], ['4575', '105', '480', ' 284', ' 623', ' 416', '2'], ['4576', '105', '488', ' 291', ' 627', ' 416', '2'], ['4577', '105', '498', ' 298', ' 634', ' 418', '2'], ['4578', '105', '506', ' 303', ' 637', ' 416', '2'], ['4579', '105', '513', ' 310', ' 638', ' 414', '2'], ['4580', '105', '522', ' 318', ' 644', ' 416', '2'], ['4581', '105', '532', ' 325', ' 650', ' 415', '2'], ['4582', '105', '542', ' 332', ' 654', ' 414', '2'], ['4583', '105', '556', ' 342', ' 659', ' 414', '2'], ['4584', '105', '563', ' 350', ' 662', ' 415', '2'], ['4585', '105', '574', ' 360', ' 663', ' 414', '2']]}, {'113': [['4813', '113', '339', ' 118', ' 370', ' 136', '2'], ['4819', '113', '340', ' 125', ' 370', ' 143', '2'], ['4821', '113', '340', ' 127', ' 369', ' 145', '2'], ['4825', '113', '338', ' 128', ' 368', ' 147', '2'], ['4826', '113', '338', ' 128', ' 368', ' 147', '2'], ['4827', '113', '338', ' 129', ' 369', ' 148', '2'], ['4828', '113', '337', ' 129', ' 371', ' 150', '2'], ['4829', '113', '337', ' 129', ' 371', ' 151', '2'], ['4830', '113', '338', ' 130', ' 372', ' 152', '2'], ['4831', '113', '338', ' 132', ' 372', ' 153', '2'], ['4832', '113', '339', ' 134', ' 371', ' 154', '2'], ['4833', '113', '339', ' 134', ' 372', ' 155', '2'], ['4834', '113', '338', ' 135', ' 373', ' 156', '2'], ['4835', '113', '337', ' 135', ' 374', ' 157', '2'], ['4836', '113', '336', ' 135', ' 373', ' 158', '2'], ['4837', '113', '336', ' 136', ' 373', ' 159', '2'], ['4838', '113', '336', ' 137', ' 373', ' 160', '2'], ['4839', '113', '338', ' 140', ' 372', ' 162', '2'], ['4840', '113', '336', ' 139', ' 375', ' 164', '2'], ['4841', '113', '335', ' 139', ' 375', ' 165', '2'], ['4842', '113', '335', ' 140', ' 375', ' 166', '2'], ['4843', '113', '335', ' 141', ' 377', ' 169', '2'], ['4844', '113', '334', ' 141', ' 378', ' 170', '2'], ['4845', '113', '334', ' 142', ' 378', ' 172', '2'], ['4846', '113', '334', ' 143', ' 378', ' 173', '2'], ['4847', '113', '333', ' 144', ' 377', ' 175', '2'], ['4848', '113', '332', ' 143', ' 382', ' 178', '2'], ['4849', '113', '333', ' 145', ' 381', ' 179', '2'], ['4850', '113', '332', ' 147', ' 379', ' 181', '2'], ['4851', '113', '331', ' 148', ' 380', ' 183', '2'], ['4852', '113', '331', ' 149', ' 379', ' 185', '2'], ['4853', '113', '330', ' 149', ' 379', ' 186', '2'], ['4854', '113', '331', ' 150', ' 379', ' 187', '2'], ['4855', '113', '331', ' 151', ' 380', ' 189', '2'], ['4856', '113', '333', ' 154', ' 381', ' 191', '2'], ['4857', '113', '333', ' 155', ' 381', ' 193', '2'], ['4858', '113', '332', ' 157', ' 381', ' 196', '2'], ['4859', '113', '332', ' 159', ' 382', ' 199', '2'], ['4860', '113', '332', ' 160', ' 382', ' 201', '2'], ['4861', '113', '332', ' 163', ' 383', ' 204', '2'], ['4862', '113', '333', ' 166', ' 383', ' 206', '2'], ['4863', '113', '333', ' 168', ' 383', ' 209', '2'], ['4864', '113', '333', ' 170', ' 383', ' 211', '2'], ['4865', '113', '332', ' 172', ' 385', ' 215', '2'], ['4866', '113', '331', ' 173', ' 385', ' 218', '2'], ['4867', '113', '330', ' 175', ' 386', ' 222', '2'], ['4868', '113', '330', ' 176', ' 388', ' 225', '2'], ['4869', '113', '330', ' 177', ' 391', ' 228', '2'], ['4870', '113', '331', ' 181', ' 391', ' 232', '2'], ['4871', '113', '332', ' 184', ' 393', ' 236', '2'], ['4872', '113', '333', ' 189', ' 393', ' 240', '2'], ['4873', '113', '331', ' 191', ' 394', ' 245', '2'], ['4874', '113', '330', ' 193', ' 396', ' 249', '2'], ['4875', '113', '330', ' 196', ' 398', ' 255', '2'], ['4876', '113', '330', ' 200', ' 401', ' 261', '2'], ['4877', '113', '329', ' 203', ' 402', ' 267', '2'], ['4878', '113', '329', ' 208', ' 404', ' 274', '2'], ['4879', '113', '329', ' 211', ' 406', ' 279', '2'], ['4880', '113', '330', ' 215', ' 408', ' 284', '2'], ['4881', '113', '329', ' 219', ' 411', ' 292', '2'], ['4882', '113', '329', ' 223', ' 414', ' 299', '2'], ['4883', '113', '329', ' 228', ' 416', ' 306', '2'], ['4884', '113', '330', ' 234', ' 420', ' 315', '2'], ['4885', '113', '331', ' 240', ' 423', ' 323', '2'], ['4886', '113', '331', ' 245', ' 427', ' 332', '2'], ['4887', '113', '331', ' 252', ' 431', ' 343', '2'], ['4888', '113', '331', ' 258', ' 435', ' 353', '2'], ['4889', '113', '331', ' 266', ' 441', ' 366', '2'], ['4890', '113', '330', ' 273', ' 445', ' 379', '2'], ['4891', '113', '329', ' 280', ' 452', ' 393', '2'], ['4892', '113', '327', ' 288', ' 457', ' 408', '2'], ['4893', '113', '330', ' 298', ' 458', ' 416', '2'], ['4894', '113', '337', ' 309', ' 459', ' 419', '2'], ['4895', '113', '347', ' 320', ' 450', ' 410', '2'], ['4896', '113', '353', ' 332', ' 450', ' 413', '2'], ['4897', '113', '361', ' 346', ' 451', ' 415', '2'], ['4898', '113', '368', ' 362', ' 446', ' 416', '2']]}, {'117': [['4846', '117', '356', ' 116', ' 384', ' 137', '2'], ['4847', '117', '356', ' 116', ' 383', ' 138', '2'], ['4848', '117', '356', ' 117', ' 383', ' 138', '2'], ['4849', '117', '356', ' 118', ' 383', ' 138', '2'], ['4850', '117', '355', ' 116', ' 384', ' 139', '2'], ['4851', '117', '354', ' 116', ' 385', ' 140', '2'], ['4853', '117', '356', ' 116', ' 384', ' 139', '2'], ['4858', '117', '356', ' 125', ' 382', ' 145', '2'], ['4861', '117', '357', ' 127', ' 383', ' 147', '2'], ['4862', '117', '357', ' 129', ' 383', ' 148', '2'], ['4863', '117', '357', ' 128', ' 384', ' 148', '2'], ['4864', '117', '356', ' 128', ' 386', ' 150', '2'], ['4865', '117', '355', ' 128', ' 387', ' 151', '2'], ['4866', '117', '355', ' 129', ' 388', ' 152', '2'], ['4867', '117', '355', ' 129', ' 388', ' 153', '2'], ['4868', '117', '356', ' 130', ' 387', ' 153', '2'], ['4869', '117', '356', ' 131', ' 387', ' 154', '2'], ['4870', '117', '355', ' 130', ' 388', ' 155', '2'], ['4871', '117', '355', ' 131', ' 389', ' 156', '2'], ['4872', '117', '354', ' 132', ' 388', ' 158', '2'], ['4873', '117', '354', ' 132', ' 389', ' 159', '2'], ['4874', '117', '355', ' 133', ' 388', ' 159', '2'], ['4875', '117', '355', ' 134', ' 388', ' 160', '2'], ['4876', '117', '355', ' 135', ' 389', ' 162', '2'], ['4877', '117', '354', ' 135', ' 390', ' 162', '2'], ['4878', '117', '354', ' 136', ' 392', ' 165', '2'], ['4879', '117', '354', ' 136', ' 393', ' 166', '2'], ['4880', '117', '356', ' 138', ' 394', ' 167', '2'], ['4881', '117', '353', ' 138', ' 393', ' 168', '2'], ['4882', '117', '354', ' 139', ' 393', ' 169', '2'], ['4883', '117', '355', ' 141', ' 395', ' 171', '2'], ['4884', '117', '354', ' 141', ' 394', ' 172', '2'], ['4885', '117', '353', ' 142', ' 395', ' 173', '2'], ['4886', '117', '354', ' 144', ' 394', ' 174', '2'], ['4887', '117', '354', ' 145', ' 393', ' 175', '2'], ['4888', '117', '354', ' 147', ' 395', ' 178', '2'], ['4889', '117', '354', ' 148', ' 395', ' 179', '2'], ['4890', '117', '354', ' 149', ' 395', ' 180', '2'], ['4891', '117', '353', ' 150', ' 395', ' 182', '2'], ['4892', '117', '353', ' 151', ' 397', ' 184', '2'], ['4893', '117', '353', ' 152', ' 397', ' 185', '2'], ['4894', '117', '352', ' 153', ' 397', ' 186', '2'], ['4895', '117', '353', ' 153', ' 399', ' 188', '2'], ['4896', '117', '353', ' 155', ' 400', ' 190', '2'], ['4897', '117', '353', ' 156', ' 400', ' 192', '2'], ['4898', '117', '353', ' 158', ' 401', ' 194', '2'], ['4899', '117', '353', ' 158', ' 401', ' 196', '2'], ['4900', '117', '353', ' 160', ' 403', ' 199', '2'], ['4901', '117', '353', ' 160', ' 404', ' 201', '2'], ['4902', '117', '353', ' 162', ' 403', ' 202', '2'], ['4903', '117', '353', ' 162', ' 404', ' 204', '2'], ['4904', '117', '353', ' 165', ' 404', ' 207', '2'], ['4905', '117', '353', ' 166', ' 405', ' 209', '2'], ['4906', '117', '353', ' 167', ' 406', ' 212', '2'], ['4907', '117', '353', ' 169', ' 406', ' 214', '2'], ['4908', '117', '354', ' 173', ' 406', ' 217', '2'], ['4909', '117', '353', ' 174', ' 407', ' 220', '2'], ['4910', '117', '354', ' 176', ' 407', ' 223', '2'], ['4911', '117', '355', ' 178', ' 410', ' 226', '2'], ['4912', '117', '354', ' 179', ' 411', ' 228', '2'], ['4913', '117', '354', ' 181', ' 412', ' 232', '2'], ['4914', '117', '353', ' 182', ' 413', ' 236', '2'], ['4915', '117', '353', ' 185', ' 414', ' 239', '2'], ['4916', '117', '354', ' 188', ' 417', ' 243', '2'], ['4917', '117', '355', ' 191', ' 418', ' 247', '2'], ['4918', '117', '355', ' 194', ' 419', ' 251', '2'], ['4919', '117', '354', ' 195', ' 421', ' 255', '2'], ['4920', '117', '354', ' 199', ' 423', ' 260', '2'], ['4921', '117', '354', ' 202', ' 423', ' 265', '2'], ['4922', '117', '353', ' 205', ' 426', ' 270', '2'], ['4923', '117', '355', ' 208', ' 428', ' 274', '2'], ['4924', '117', '356', ' 212', ' 430', ' 279', '2'], ['4925', '117', '357', ' 216', ' 433', ' 284', '2'], ['4926', '117', '355', ' 219', ' 436', ' 292', '2'], ['4927', '117', '355', ' 222', ' 439', ' 298', '2'], ['4928', '117', '356', ' 227', ' 440', ' 304', '2'], ['4929', '117', '357', ' 231', ' 444', ' 311', '2'], ['4930', '117', '357', ' 237', ' 446', ' 318', '2'], ['4931', '117', '358', ' 241', ' 449', ' 325', '2'], ['4932', '117', '357', ' 247', ' 452', ' 334', '2'], ['4933', '117', '356', ' 252', ' 456', ' 343', '2'], ['4934', '117', '357', ' 258', ' 460', ' 351', '2'], ['4935', '117', '359', ' 265', ' 465', ' 361', '2'], ['4936', '117', '358', ' 271', ' 468', ' 372', '2'], ['4937', '117', '357', ' 278', ' 474', ' 385', '2'], ['4938', '117', '356', ' 286', ' 481', ' 399', '2'], ['4939', '117', '358', ' 294', ' 486', ' 410', '2'], ['4940', '117', '362', ' 302', ' 489', ' 416', '2'], ['4941', '117', '367', ' 310', ' 489', ' 419', '2'], ['4942', '117', '378', ' 319', ' 481', ' 408', '2']]}, {'129': [['5412', '129', '378', ' 105', ' 396', ' 118', '2'], ['5413', '129', '378', ' 105', ' 396', ' 119', '2'], ['5414', '129', '379', ' 104', ' 397', ' 119', '2'], ['5415', '129', '379', ' 104', ' 397', ' 119', '2'], ['5420', '129', '379', ' 105', ' 397', ' 119', '2'], ['5422', '129', '379', ' 106', ' 398', ' 120', '2'], ['5423', '129', '380', ' 106', ' 398', ' 120', '2'], ['5424', '129', '380', ' 106', ' 399', ' 121', '2'], ['5425', '129', '380', ' 106', ' 399', ' 121', '2'], ['5426', '129', '381', ' 106', ' 399', ' 121', '2'], ['5427', '129', '381', ' 107', ' 399', ' 121', '2'], ['5428', '129', '381', ' 107', ' 400', ' 121', '2'], ['5429', '129', '382', ' 107', ' 401', ' 122', '2'], ['5430', '129', '382', ' 107', ' 401', ' 122', '2'], ['5431', '129', '381', ' 107', ' 400', ' 122', '2'], ['5432', '129', '381', ' 107', ' 401', ' 122', '2'], ['5435', '129', '382', ' 107', ' 403', ' 123', '2'], ['5436', '129', '382', ' 107', ' 404', ' 124', '2'], ['5437', '129', '382', ' 107', ' 404', ' 125', '2'], ['5440', '129', '383', ' 107', ' 405', ' 125', '2'], ['5441', '129', '384', ' 108', ' 407', ' 126', '2'], ['5442', '129', '384', ' 108', ' 407', ' 127', '2'], ['5443', '129', '385', ' 109', ' 407', ' 127', '2'], ['5444', '129', '385', ' 109', ' 407', ' 127', '2'], ['5445', '129', '385', ' 110', ' 407', ' 128', '2'], ['5446', '129', '386', ' 110', ' 407', ' 127', '2'], ['5447', '129', '386', ' 111', ' 407', ' 127', '2'], ['5448', '129', '386', ' 111', ' 407', ' 128', '2'], ['5449', '129', '386', ' 111', ' 407', ' 128', '2'], ['5450', '129', '386', ' 112', ' 407', ' 129', '2'], ['5451', '129', '385', ' 111', ' 408', ' 129', '2'], ['5452', '129', '386', ' 111', ' 408', ' 129', '2'], ['5453', '129', '386', ' 111', ' 409', ' 129', '2'], ['5454', '129', '386', ' 111', ' 409', ' 130', '2'], ['5455', '129', '386', ' 111', ' 409', ' 130', '2'], ['5456', '129', '386', ' 111', ' 410', ' 131', '2'], ['5457', '129', '387', ' 112', ' 410', ' 132', '2'], ['5458', '129', '387', ' 112', ' 410', ' 132', '2'], ['5459', '129', '387', ' 113', ' 410', ' 133', '2'], ['5460', '129', '388', ' 114', ' 411', ' 133', '2'], ['5461', '129', '388', ' 114', ' 411', ' 134', '2'], ['5462', '129', '388', ' 115', ' 411', ' 134', '2'], ['5463', '129', '389', ' 115', ' 412', ' 135', '2'], ['5464', '129', '389', ' 116', ' 412', ' 135', '2'], ['5465', '129', '389', ' 116', ' 412', ' 135', '2'], ['5466', '129', '390', ' 116', ' 412', ' 134', '2'], ['5467', '129', '391', ' 116', ' 412', ' 134', '2'], ['5468', '129', '391', ' 117', ' 412', ' 134', '2'], ['5469', '129', '390', ' 117', ' 413', ' 136', '2'], ['5470', '129', '391', ' 117', ' 414', ' 137', '2'], ['5471', '129', '392', ' 118', ' 415', ' 138', '2'], ['5472', '129', '392', ' 118', ' 416', ' 138', '2'], ['5473', '129', '393', ' 118', ' 417', ' 139', '2'], ['5474', '129', '394', ' 118', ' 419', ' 139', '2'], ['5475', '129', '394', ' 118', ' 419', ' 140', '2'], ['5476', '129', '394', ' 119', ' 420', ' 140', '2'], ['5477', '129', '394', ' 117', ' 421', ' 141', '2'], ['5478', '129', '394', ' 118', ' 421', ' 141', '2'], ['5479', '129', '396', ' 119', ' 421', ' 142', '2'], ['5480', '129', '396', ' 120', ' 422', ' 142', '2'], ['5481', '129', '396', ' 120', ' 422', ' 143', '2'], ['5482', '129', '396', ' 120', ' 422', ' 143', '2'], ['5483', '129', '396', ' 121', ' 422', ' 144', '2'], ['5484', '129', '396', ' 122', ' 422', ' 145', '2'], ['5485', '129', '397', ' 123', ' 423', ' 146', '2'], ['5486', '129', '398', ' 124', ' 423', ' 146', '2'], ['5487', '129', '398', ' 125', ' 423', ' 147', '2'], ['5488', '129', '399', ' 125', ' 424', ' 147', '2'], ['5489', '129', '400', ' 125', ' 425', ' 147', '2'], ['5490', '129', '400', ' 126', ' 426', ' 147', '2'], ['5491', '129', '401', ' 126', ' 427', ' 148', '2'], ['5492', '129', '401', ' 127', ' 429', ' 150', '2'], ['5493', '129', '400', ' 126', ' 430', ' 151', '2'], ['5494', '129', '400', ' 127', ' 431', ' 152', '2'], ['5495', '129', '400', ' 126', ' 433', ' 152', '2'], ['5496', '129', '401', ' 126', ' 434', ' 153', '2'], ['5497', '129', '402', ' 127', ' 435', ' 154', '2'], ['5498', '129', '402', ' 127', ' 436', ' 154', '2'], ['5499', '129', '404', ' 127', ' 437', ' 155', '2'], ['5500', '129', '404', ' 128', ' 437', ' 155', '2'], ['5501', '129', '405', ' 129', ' 438', ' 156', '2'], ['5502', '129', '406', ' 130', ' 438', ' 157', '2'], ['5503', '129', '405', ' 130', ' 440', ' 158', '2'], ['5504', '129', '406', ' 129', ' 440', ' 158', '2'], ['5505', '129', '407', ' 129', ' 441', ' 159', '2'], ['5506', '129', '408', ' 130', ' 442', ' 159', '2'], ['5507', '129', '409', ' 131', ' 443', ' 160', '2'], ['5508', '129', '410', ' 133', ' 444', ' 161', '2'], ['5509', '129', '411', ' 133', ' 446', ' 163', '2'], ['5510', '129', '412', ' 135', ' 446', ' 164', '2'], ['5511', '129', '413', ' 136', ' 448', ' 164', '2'], ['5512', '129', '414', ' 136', ' 449', ' 165', '2'], ['5513', '129', '414', ' 135', ' 451', ' 166', '2'], ['5514', '129', '415', ' 136', ' 452', ' 167', '2'], ['5515', '129', '415', ' 137', ' 452', ' 168', '2'], ['5516', '129', '416', ' 138', ' 452', ' 169', '2'], ['5517', '129', '416', ' 139', ' 454', ' 171', '2'], ['5518', '129', '417', ' 139', ' 455', ' 172', '2'], ['5519', '129', '418', ' 140', ' 456', ' 174', '2'], ['5520', '129', '419', ' 141', ' 458', ' 175', '2'], ['5521', '129', '420', ' 142', ' 459', ' 176', '2'], ['5522', '129', '422', ' 143', ' 461', ' 178', '2'], ['5523', '129', '422', ' 144', ' 461', ' 179', '2'], ['5524', '129', '423', ' 145', ' 463', ' 180', '2'], ['5525', '129', '424', ' 145', ' 463', ' 181', '2'], ['5526', '129', '425', ' 147', ' 464', ' 182', '2'], ['5527', '129', '426', ' 148', ' 465', ' 183', '2'], ['5528', '129', '428', ' 148', ' 468', ' 184', '2'], ['5529', '129', '429', ' 149', ' 469', ' 185', '2'], ['5530', '129', '431', ' 150', ' 470', ' 186', '2'], ['5531', '129', '432', ' 152', ' 472', ' 188', '2'], ['5532', '129', '434', ' 152', ' 475', ' 189', '2'], ['5533', '129', '434', ' 153', ' 476', ' 191', '2'], ['5534', '129', '435', ' 154', ' 477', ' 193', '2'], ['5535', '129', '436', ' 155', ' 479', ' 194', '2'], ['5536', '129', '437', ' 156', ' 481', ' 196', '2'], ['5537', '129', '439', ' 157', ' 483', ' 198', '2'], ['5538', '129', '441', ' 158', ' 485', ' 199', '2'], ['5539', '129', '441', ' 159', ' 487', ' 202', '2'], ['5540', '129', '442', ' 160', ' 489', ' 204', '2'], ['5541', '129', '443', ' 161', ' 490', ' 205', '2'], ['5542', '129', '445', ' 163', ' 493', ' 206', '2'], ['5543', '129', '446', ' 163', ' 495', ' 208', '2'], ['5544', '129', '448', ' 165', ' 496', ' 208', '2'], ['5545', '129', '449', ' 166', ' 498', ' 212', '2'], ['5546', '129', '450', ' 168', ' 501', ' 214', '2'], ['5547', '129', '451', ' 168', ' 504', ' 216', '2'], ['5548', '129', '452', ' 169', ' 506', ' 218', '2'], ['5549', '129', '453', ' 171', ' 508', ' 221', '2'], ['5550', '129', '456', ' 174', ' 510', ' 224', '2'], ['5551', '129', '458', ' 176', ' 513', ' 226', '2'], ['5552', '129', '458', ' 176', ' 516', ' 229', '2'], ['5553', '129', '461', ' 177', ' 518', ' 231', '2'], ['5554', '129', '463', ' 179', ' 521', ' 233', '2'], ['5555', '129', '464', ' 180', ' 524', ' 235', '2'], ['5556', '129', '466', ' 182', ' 527', ' 239', '2'], ['5557', '129', '468', ' 183', ' 531', ' 243', '2'], ['5558', '129', '470', ' 185', ' 534', ' 245', '2'], ['5559', '129', '472', ' 188', ' 537', ' 248', '2'], ['5560', '129', '477', ' 193', ' 539', ' 251', '2'], ['5561', '129', '477', ' 192', ' 543', ' 255', '2'], ['5562', '129', '479', ' 194', ' 547', ' 257', '2'], ['5563', '129', '482', ' 196', ' 551', ' 260', '2'], ['5564', '129', '484', ' 197', ' 555', ' 262', '2'], ['5565', '129', '486', ' 199', ' 559', ' 267', '2'], ['5566', '129', '488', ' 201', ' 563', ' 272', '2'], ['5567', '129', '491', ' 202', ' 568', ' 274', '2'], ['5568', '129', '493', ' 205', ' 571', ' 278', '2'], ['5569', '129', '497', ' 208', ' 575', ' 282', '2'], ['5570', '129', '501', ' 212', ' 579', ' 285', '2'], ['5571', '129', '504', ' 215', ' 584', ' 290', '2'], ['5572', '129', '507', ' 217', ' 590', ' 296', '2'], ['5573', '129', '512', ' 221', ' 596', ' 300', '2'], ['5574', '129', '515', ' 223', ' 604', ' 306', '2'], ['5575', '129', '519', ' 226', ' 610', ' 311', '2'], ['5576', '129', '522', ' 229', ' 614', ' 316', '2'], ['5577', '129', '526', ' 232', ' 621', ' 323', '2'], ['5578', '129', '530', ' 236', ' 628', ' 329', '2'], ['5579', '129', '535', ' 241', ' 634', ' 335', '2'], ['5580', '129', '540', ' 245', ' 641', ' 341', '2'], ['5581', '129', '545', ' 248', ' 649', ' 347', '2'], ['5582', '129', '549', ' 252', ' 657', ' 354', '2'], ['5583', '129', '554', ' 256', ' 665', ' 362', '2'], ['5584', '129', '560', ' 261', ' 674', ' 369', '2'], ['5585', '129', '565', ' 266', ' 683', ' 378', '2'], ['5586', '129', '570', ' 270', ' 693', ' 386', '2'], ['5587', '129', '577', ' 275', ' 703', ' 396', '2'], ['5588', '129', '582', ' 280', ' 715', ' 407', '2'], ['5589', '129', '590', ' 286', ' 723', ' 413', '2'], ['5590', '129', '601', ' 292', ' 733', ' 417', '2'], ['5591', '129', '613', ' 299', ' 741', ' 417', '2'], ['5592', '129', '624', ' 305', ' 751', ' 419', '2'], ['5593', '129', '634', ' 312', ' 755', ' 417', '2'], ['5594', '129', '642', ' 320', ' 758', ' 418', '2'], ['5595', '129', '651', ' 327', ' 762', ' 417', '2'], ['5596', '129', '660', ' 335', ' 763', ' 416', '2'], ['5597', '129', '669', ' 344', ' 763', ' 415', '2']]}, {'134': [['5574', '134', '391', ' 111', ' 415', ' 132', '2'], ['5575', '134', '392', ' 114', ' 413', ' 132', '2'], ['5576', '134', '393', ' 115', ' 414', ' 132', '2'], ['5577', '134', '394', ' 115', ' 414', ' 132', '2'], ['5578', '134', '394', ' 114', ' 416', ' 132', '2'], ['5579', '134', '395', ' 115', ' 417', ' 132', '2'], ['5580', '134', '397', ' 116', ' 418', ' 133', '2'], ['5581', '134', '396', ' 115', ' 419', ' 133', '2'], ['5582', '134', '397', ' 116', ' 420', ' 134', '2'], ['5583', '134', '398', ' 116', ' 420', ' 134', '2'], ['5584', '134', '399', ' 117', ' 421', ' 134', '2'], ['5585', '134', '399', ' 118', ' 422', ' 135', '2'], ['5586', '134', '400', ' 118', ' 423', ' 136', '2'], ['5587', '134', '400', ' 120', ' 423', ' 137', '2'], ['5588', '134', '401', ' 120', ' 424', ' 138', '2'], ['5589', '134', '402', ' 120', ' 427', ' 139', '2'], ['5590', '134', '403', ' 119', ' 428', ' 139', '2'], ['5591', '134', '403', ' 119', ' 429', ' 140', '2'], ['5592', '134', '405', ' 120', ' 430', ' 140', '2'], ['5593', '134', '404', ' 119', ' 431', ' 141', '2'], ['5594', '134', '405', ' 121', ' 431', ' 141', '2'], ['5595', '134', '406', ' 122', ' 432', ' 142', '2'], ['5596', '134', '408', ' 123', ' 433', ' 142', '2'], ['5597', '134', '409', ' 124', ' 433', ' 142', '2'], ['5598', '134', '409', ' 124', ' 434', ' 143', '2'], ['5599', '134', '409', ' 123', ' 437', ' 145', '2'], ['5600', '134', '409', ' 123', ' 438', ' 145', '2'], ['5601', '134', '410', ' 124', ' 439', ' 145', '2'], ['5602', '134', '411', ' 125', ' 440', ' 146', '2'], ['5603', '134', '413', ' 127', ' 440', ' 146', '2'], ['5604', '134', '415', ' 129', ' 440', ' 147', '2'], ['5605', '134', '414', ' 128', ' 444', ' 149', '2'], ['5606', '134', '415', ' 128', ' 446', ' 150', '2'], ['5607', '134', '415', ' 128', ' 448', ' 151', '2'], ['5608', '134', '416', ' 129', ' 449', ' 152', '2'], ['5609', '134', '417', ' 130', ' 449', ' 152', '2'], ['5610', '134', '417', ' 130', ' 450', ' 153', '2'], ['5611', '134', '417', ' 131', ' 451', ' 154', '2'], ['5612', '134', '417', ' 131', ' 452', ' 156', '2'], ['5613', '134', '418', ' 132', ' 453', ' 156', '2'], ['5614', '134', '419', ' 132', ' 454', ' 157', '2'], ['5615', '134', '419', ' 132', ' 455', ' 158', '2'], ['5616', '134', '420', ' 134', ' 456', ' 159', '2'], ['5617', '134', '420', ' 134', ' 457', ' 161', '2'], ['5618', '134', '421', ' 135', ' 459', ' 162', '2'], ['5619', '134', '421', ' 135', ' 460', ' 163', '2'], ['5620', '134', '422', ' 135', ' 462', ' 164', '2'], ['5621', '134', '423', ' 136', ' 462', ' 165', '2'], ['5622', '134', '424', ' 137', ' 463', ' 166', '2'], ['5623', '134', '425', ' 138', ' 465', ' 167', '2'], ['5624', '134', '426', ' 139', ' 466', ' 168', '2'], ['5625', '134', '427', ' 140', ' 468', ' 171', '2'], ['5626', '134', '426', ' 141', ' 469', ' 172', '2'], ['5627', '134', '427', ' 141', ' 471', ' 173', '2'], ['5628', '134', '428', ' 142', ' 471', ' 174', '2'], ['5629', '134', '431', ' 144', ' 473', ' 176', '2'], ['5630', '134', '432', ' 145', ' 475', ' 177', '2'], ['5631', '134', '433', ' 146', ' 475', ' 179', '2'], ['5632', '134', '433', ' 147', ' 477', ' 181', '2'], ['5633', '134', '434', ' 148', ' 479', ' 182', '2'], ['5634', '134', '436', ' 150', ' 479', ' 183', '2'], ['5635', '134', '436', ' 150', ' 481', ' 185', '2'], ['5636', '134', '438', ' 153', ' 480', ' 186', '2'], ['5637', '134', '440', ' 156', ' 482', ' 189', '2'], ['5638', '134', '442', ' 157', ' 484', ' 190', '2'], ['5639', '134', '441', ' 157', ' 486', ' 192', '2'], ['5640', '134', '442', ' 158', ' 488', ' 194', '2'], ['5641', '134', '443', ' 160', ' 489', ' 196', '2'], ['5642', '134', '444', ' 161', ' 491', ' 197', '2'], ['5643', '134', '444', ' 161', ' 494', ' 200', '2'], ['5644', '134', '446', ' 163', ' 497', ' 203', '2'], ['5645', '134', '446', ' 165', ' 498', ' 205', '2'], ['5646', '134', '448', ' 167', ' 500', ' 208', '2'], ['5647', '134', '449', ' 168', ' 502', ' 210', '2'], ['5648', '134', '450', ' 170', ' 505', ' 212', '2'], ['5649', '134', '452', ' 172', ' 506', ' 215', '2'], ['5650', '134', '453', ' 174', ' 508', ' 217', '2'], ['5651', '134', '454', ' 176', ' 511', ' 220', '2'], ['5652', '134', '455', ' 178', ' 513', ' 224', '2'], ['5653', '134', '456', ' 180', ' 516', ' 227', '2'], ['5654', '134', '457', ' 180', ' 519', ' 229', '2'], ['5655', '134', '458', ' 182', ' 521', ' 232', '2'], ['5656', '134', '460', ' 185', ' 525', ' 237', '2'], ['5657', '134', '461', ' 188', ' 527', ' 239', '2'], ['5658', '134', '465', ' 191', ' 531', ' 243', '2'], ['5659', '134', '466', ' 194', ' 533', ' 246', '2'], ['5660', '134', '468', ' 196', ' 537', ' 250', '2'], ['5661', '134', '469', ' 198', ' 541', ' 255', '2'], ['5662', '134', '471', ' 201', ' 543', ' 258', '2'], ['5663', '134', '473', ' 203', ' 548', ' 262', '2'], ['5664', '134', '474', ' 206', ' 553', ' 268', '2'], ['5665', '134', '477', ' 210', ' 556', ' 272', '2'], ['5666', '134', '479', ' 212', ' 561', ' 278', '2'], ['5667', '134', '482', ' 217', ' 567', ' 284', '2'], ['5668', '134', '484', ' 220', ' 571', ' 289', '2'], ['5669', '134', '487', ' 223', ' 577', ' 295', '2'], ['5670', '134', '491', ' 228', ' 582', ' 300', '2'], ['5671', '134', '493', ' 230', ' 588', ' 307', '2'], ['5672', '134', '496', ' 234', ' 594', ' 313', '2'], ['5673', '134', '500', ' 240', ' 601', ' 320', '2'], ['5674', '134', '503', ' 244', ' 607', ' 328', '2'], ['5675', '134', '506', ' 249', ' 614', ' 336', '2'], ['5676', '134', '511', ' 254', ' 622', ' 344', '2'], ['5677', '134', '516', ' 259', ' 631', ' 352', '2'], ['5678', '134', '521', ' 266', ' 639', ' 362', '2'], ['5679', '134', '526', ' 272', ' 650', ' 373', '2'], ['5680', '134', '530', ' 277', ' 660', ' 384', '2'], ['5681', '134', '534', ' 284', ' 671', ' 397', '2'], ['5682', '134', '540', ' 292', ' 682', ' 409', '2'], ['5683', '134', '551', ' 301', ' 690', ' 415', '2'], ['5684', '134', '563', ' 309', ' 698', ' 417', '2'], ['5685', '134', '577', ' 317', ' 709', ' 419', '2'], ['5686', '134', '588', ' 326', ' 710', ' 415', '2'], ['5687', '134', '600', ' 339', ' 710', ' 416', '2'], ['5688', '134', '614', ' 349', ' 714', ' 415', '2'], ['5689', '134', '627', ' 362', ' 715', ' 415', '2']]}, {'130': [['5507', '130', '344', ' 105', ' 368', ' 122', '2'], ['5508', '130', '344', ' 105', ' 368', ' 122', '2'], ['5509', '130', '343', ' 105', ' 369', ' 123', '2'], ['5510', '130', '344', ' 105', ' 369', ' 123', '2'], ['5511', '130', '344', ' 105', ' 369', ' 124', '2'], ['5512', '130', '344', ' 105', ' 370', ' 124', '2'], ['5521', '130', '347', ' 107', ' 371', ' 125', '2'], ['5522', '130', '346', ' 108', ' 371', ' 125', '2'], ['5523', '130', '347', ' 108', ' 371', ' 126', '2'], ['5524', '130', '347', ' 109', ' 371', ' 126', '2'], ['5525', '130', '347', ' 109', ' 371', ' 126', '2'], ['5526', '130', '348', ' 109', ' 371', ' 126', '2'], ['5527', '130', '348', ' 109', ' 371', ' 126', '2'], ['5528', '130', '348', ' 109', ' 372', ' 126', '2'], ['5529', '130', '348', ' 109', ' 372', ' 126', '2'], ['5530', '130', '348', ' 109', ' 373', ' 126', '2'], ['5531', '130', '348', ' 108', ' 373', ' 126', '2'], ['5532', '130', '349', ' 109', ' 372', ' 127', '2'], ['5533', '130', '349', ' 109', ' 372', ' 127', '2'], ['5534', '130', '349', ' 109', ' 373', ' 127', '2'], ['5535', '130', '348', ' 109', ' 373', ' 127', '2'], ['5536', '130', '349', ' 109', ' 373', ' 127', '2'], ['5537', '130', '348', ' 109', ' 373', ' 127', '2'], ['5538', '130', '349', ' 108', ' 374', ' 127', '2'], ['5539', '130', '349', ' 109', ' 375', ' 128', '2'], ['5540', '130', '349', ' 109', ' 375', ' 129', '2'], ['5541', '130', '349', ' 109', ' 375', ' 129', '2'], ['5542', '130', '349', ' 109', ' 375', ' 129', '2'], ['5543', '130', '349', ' 109', ' 375', ' 129', '2'], ['5544', '130', '349', ' 110', ' 375', ' 129', '2'], ['5545', '130', '349', ' 110', ' 375', ' 130', '2'], ['5546', '130', '349', ' 110', ' 375', ' 130', '2'], ['5547', '130', '350', ' 110', ' 376', ' 130', '2'], ['5548', '130', '350', ' 110', ' 376', ' 130', '2'], ['5549', '130', '351', ' 111', ' 376', ' 131', '2'], ['5550', '130', '350', ' 111', ' 376', ' 131', '2'], ['5551', '130', '351', ' 111', ' 376', ' 132', '2'], ['5552', '130', '351', ' 112', ' 376', ' 132', '2'], ['5553', '130', '351', ' 111', ' 377', ' 132', '2'], ['5554', '130', '351', ' 111', ' 377', ' 132', '2'], ['5555', '130', '352', ' 112', ' 377', ' 133', '2'], ['5556', '130', '352', ' 113', ' 378', ' 133', '2'], ['5557', '130', '353', ' 113', ' 379', ' 134', '2'], ['5558', '130', '353', ' 113', ' 379', ' 134', '2'], ['5559', '130', '353', ' 113', ' 379', ' 134', '2'], ['5560', '130', '353', ' 113', ' 380', ' 134', '2'], ['5561', '130', '352', ' 112', ' 381', ' 134', '2'], ['5562', '130', '353', ' 112', ' 381', ' 135', '2'], ['5563', '130', '353', ' 112', ' 382', ' 135', '2'], ['5564', '130', '353', ' 111', ' 383', ' 135', '2'], ['5565', '130', '353', ' 112', ' 383', ' 136', '2'], ['5566', '130', '353', ' 113', ' 383', ' 137', '2'], ['5567', '130', '353', ' 112', ' 384', ' 137', '2'], ['5568', '130', '354', ' 113', ' 384', ' 138', '2'], ['5570', '130', '354', ' 114', ' 384', ' 139', '2'], ['5571', '130', '354', ' 114', ' 385', ' 139', '2'], ['5572', '130', '354', ' 113', ' 386', ' 139', '2'], ['5573', '130', '354', ' 114', ' 386', ' 140', '2'], ['5574', '130', '354', ' 114', ' 386', ' 141', '2'], ['5575', '130', '355', ' 115', ' 386', ' 141', '2'], ['5576', '130', '354', ' 115', ' 386', ' 141', '2'], ['5577', '130', '354', ' 115', ' 386', ' 142', '2'], ['5578', '130', '354', ' 115', ' 385', ' 141', '2'], ['5579', '130', '355', ' 115', ' 386', ' 142', '2'], ['5580', '130', '355', ' 115', ' 386', ' 142', '2'], ['5581', '130', '354', ' 115', ' 386', ' 142', '2'], ['5582', '130', '355', ' 115', ' 386', ' 143', '2'], ['5583', '130', '355', ' 115', ' 385', ' 143', '2'], ['5584', '130', '356', ' 117', ' 385', ' 144', '2'], ['5585', '130', '356', ' 118', ' 384', ' 144', '2'], ['5586', '130', '357', ' 119', ' 384', ' 144', '2'], ['5587', '130', '357', ' 120', ' 384', ' 145', '2'], ['5588', '130', '358', ' 121', ' 385', ' 146', '2'], ['5589', '130', '358', ' 122', ' 384', ' 146', '2'], ['5590', '130', '358', ' 123', ' 384', ' 147', '2'], ['5591', '130', '358', ' 124', ' 384', ' 147', '2'], ['5592', '130', '358', ' 125', ' 384', ' 148', '2'], ['5593', '130', '358', ' 126', ' 384', ' 148', '2'], ['5594', '130', '359', ' 126', ' 384', ' 148', '2'], ['5595', '130', '359', ' 126', ' 385', ' 149', '2'], ['5596', '130', '358', ' 127', ' 386', ' 150', '2'], ['5597', '130', '358', ' 127', ' 387', ' 150', '2'], ['5598', '130', '357', ' 126', ' 387', ' 151', '2'], ['5599', '130', '358', ' 127', ' 387', ' 151', '2'], ['5600', '130', '358', ' 127', ' 387', ' 151', '2'], ['5601', '130', '357', ' 127', ' 388', ' 152', '2'], ['5602', '130', '357', ' 127', ' 388', ' 152', '2'], ['5603', '130', '357', ' 127', ' 388', ' 152', '2'], ['5604', '130', '358', ' 128', ' 388', ' 153', '2'], ['5605', '130', '357', ' 128', ' 389', ' 154', '2'], ['5606', '130', '358', ' 129', ' 390', ' 155', '2'], ['5607', '130', '358', ' 129', ' 390', ' 155', '2'], ['5608', '130', '358', ' 130', ' 390', ' 156', '2'], ['5609', '130', '357', ' 130', ' 391', ' 157', '2'], ['5610', '130', '357', ' 130', ' 392', ' 158', '2'], ['5611', '130', '358', ' 131', ' 392', ' 159', '2'], ['5612', '130', '358', ' 133', ' 392', ' 160', '2'], ['5613', '130', '359', ' 133', ' 393', ' 161', '2'], ['5614', '130', '359', ' 134', ' 393', ' 161', '2'], ['5615', '130', '360', ' 134', ' 394', ' 162', '2'], ['5616', '130', '359', ' 135', ' 394', ' 162', '2'], ['5617', '130', '359', ' 136', ' 396', ' 164', '2'], ['5618', '130', '359', ' 136', ' 397', ' 165', '2'], ['5619', '130', '359', ' 136', ' 397', ' 166', '2'], ['5620', '130', '358', ' 136', ' 397', ' 167', '2'], ['5621', '130', '359', ' 136', ' 398', ' 167', '2'], ['5622', '130', '359', ' 137', ' 398', ' 168', '2'], ['5623', '130', '359', ' 137', ' 399', ' 169', '2'], ['5624', '130', '359', ' 138', ' 399', ' 170', '2'], ['5625', '130', '359', ' 138', ' 399', ' 171', '2'], ['5626', '130', '359', ' 138', ' 400', ' 172', '2'], ['5627', '130', '359', ' 139', ' 400', ' 173', '2'], ['5628', '130', '359', ' 139', ' 401', ' 173', '2'], ['5629', '130', '360', ' 139', ' 401', ' 174', '2'], ['5630', '130', '359', ' 140', ' 402', ' 176', '2'], ['5631', '130', '360', ' 140', ' 402', ' 177', '2'], ['5632', '130', '361', ' 143', ' 401', ' 178', '2'], ['5633', '130', '361', ' 144', ' 401', ' 179', '2'], ['5634', '130', '360', ' 144', ' 402', ' 180', '2'], ['5635', '130', '360', ' 145', ' 402', ' 182', '2'], ['5636', '130', '360', ' 146', ' 402', ' 182', '2'], ['5637', '130', '361', ' 147', ' 403', ' 183', '2'], ['5638', '130', '361', ' 148', ' 404', ' 184', '2'], ['5639', '130', '361', ' 148', ' 404', ' 185', '2'], ['5640', '130', '360', ' 148', ' 405', ' 187', '2'], ['5641', '130', '360', ' 149', ' 406', ' 189', '2'], ['5642', '130', '361', ' 151', ' 407', ' 190', '2'], ['5643', '130', '362', ' 151', ' 408', ' 191', '2'], ['5644', '130', '362', ' 153', ' 409', ' 193', '2'], ['5645', '130', '363', ' 154', ' 409', ' 194', '2'], ['5646', '130', '364', ' 156', ' 409', ' 195', '2'], ['5647', '130', '363', ' 157', ' 410', ' 197', '2'], ['5648', '130', '363', ' 158', ' 411', ' 199', '2'], ['5649', '130', '364', ' 159', ' 412', ' 200', '2'], ['5650', '130', '364', ' 160', ' 413', ' 202', '2'], ['5651', '130', '365', ' 161', ' 413', ' 203', '2'], ['5652', '130', '365', ' 163', ' 414', ' 205', '2'], ['5653', '130', '365', ' 164', ' 415', ' 207', '2'], ['5654', '130', '365', ' 164', ' 417', ' 209', '2'], ['5655', '130', '365', ' 165', ' 418', ' 211', '2'], ['5656', '130', '365', ' 166', ' 418', ' 212', '2'], ['5657', '130', '366', ' 167', ' 419', ' 213', '2'], ['5658', '130', '367', ' 168', ' 420', ' 215', '2'], ['5659', '130', '367', ' 169', ' 422', ' 217', '2'], ['5660', '130', '368', ' 171', ' 423', ' 220', '2'], ['5661', '130', '367', ' 173', ' 424', ' 224', '2'], ['5662', '130', '368', ' 175', ' 425', ' 226', '2'], ['5663', '130', '369', ' 176', ' 427', ' 227', '2'], ['5664', '130', '371', ' 177', ' 428', ' 228', '2'], ['5665', '130', '372', ' 178', ' 430', ' 230', '2'], ['5666', '130', '371', ' 180', ' 431', ' 233', '2'], ['5667', '130', '371', ' 182', ' 432', ' 236', '2'], ['5668', '130', '372', ' 184', ' 434', ' 239', '2'], ['5669', '130', '373', ' 186', ' 435', ' 242', '2'], ['5670', '130', '373', ' 187', ' 438', ' 245', '2'], ['5671', '130', '374', ' 189', ' 441', ' 249', '2'], ['5672', '130', '375', ' 192', ' 443', ' 253', '2'], ['5673', '130', '376', ' 194', ' 443', ' 255', '2'], ['5674', '130', '377', ' 196', ' 445', ' 257', '2'], ['5675', '130', '379', ' 199', ' 448', ' 261', '2'], ['5676', '130', '380', ' 200', ' 451', ' 264', '2'], ['5677', '130', '381', ' 202', ' 453', ' 268', '2'], ['5678', '130', '382', ' 204', ' 455', ' 271', '2'], ['5679', '130', '383', ' 206', ' 458', ' 274', '2'], ['5680', '130', '383', ' 208', ' 459', ' 278', '2'], ['5681', '130', '384', ' 210', ' 463', ' 282', '2'], ['5682', '130', '386', ' 213', ' 467', ' 287', '2'], ['5683', '130', '388', ' 215', ' 468', ' 289', '2'], ['5684', '130', '390', ' 218', ' 471', ' 293', '2'], ['5685', '130', '390', ' 219', ' 474', ' 298', '2'], ['5688', '130', '392', ' 225', ' 486', ' 313', '2'], ['5689', '130', '393', ' 227', ' 491', ' 319', '2'], ['5690', '130', '395', ' 229', ' 495', ' 325', '2'], ['5691', '130', '396', ' 233', ' 498', ' 329', '2'], ['5692', '130', '399', ' 239', ' 503', ' 337', '2'], ['5693', '130', '402', ' 243', ' 506', ' 341', '2'], ['5694', '130', '404', ' 247', ' 511', ' 348', '2'], ['5695', '130', '407', ' 252', ' 517', ' 356', '2'], ['5696', '130', '408', ' 255', ' 522', ' 362', '2'], ['5697', '130', '409', ' 260', ' 528', ' 371', '2'], ['5698', '130', '412', ' 264', ' 535', ' 379', '2'], ['5699', '130', '414', ' 268', ' 542', ' 388', '2'], ['5700', '130', '414', ' 274', ' 550', ' 401', '2'], ['5701', '130', '417', ' 279', ' 557', ' 409', '2'], ['5702', '130', '424', ' 284', ' 564', ' 414', '2'], ['5703', '130', '432', ' 290', ' 568', ' 415', '2'], ['5704', '130', '439', ' 297', ' 572', ' 417', '2'], ['5705', '130', '445', ' 303', ' 575', ' 417', '2'], ['5706', '130', '453', ' 310', ' 579', ' 417', '2'], ['5707', '130', '460', ' 318', ' 581', ' 416', '2'], ['5708', '130', '468', ' 324', ' 585', ' 416', '2'], ['5709', '130', '476', ' 330', ' 591', ' 416', '2'], ['5710', '130', '483', ' 341', ' 589', ' 416', '2'], ['5711', '130', '492', ' 351', ' 589', ' 415', '2']]}, {'144': [['6466', '144', '351', ' 113', ' 374', ' 132', '2'], ['6467', '144', '351', ' 114', ' 374', ' 132', '2'], ['6470', '144', '350', ' 113', ' 376', ' 133', '2'], ['6471', '144', '350', ' 113', ' 376', ' 134', '2'], ['6472', '144', '351', ' 116', ' 376', ' 134', '2'], ['6473', '144', '351', ' 117', ' 376', ' 135', '2'], ['6474', '144', '351', ' 115', ' 377', ' 135', '2'], ['6475', '144', '351', ' 116', ' 377', ' 136', '2'], ['6476', '144', '352', ' 118', ' 377', ' 136', '2'], ['6477', '144', '352', ' 118', ' 378', ' 137', '2'], ['6478', '144', '351', ' 118', ' 378', ' 137', '2'], ['6481', '144', '351', ' 118', ' 379', ' 139', '2'], ['6482', '144', '349', ' 116', ' 382', ' 140', '2'], ['6483', '144', '349', ' 117', ' 382', ' 141', '2'], ['6484', '144', '349', ' 117', ' 383', ' 142', '2'], ['6486', '144', '349', ' 117', ' 384', ' 142', '2'], ['6487', '144', '349', ' 117', ' 385', ' 143', '2'], ['6488', '144', '350', ' 119', ' 384', ' 144', '2'], ['6489', '144', '352', ' 123', ' 383', ' 145', '2'], ['6490', '144', '353', ' 125', ' 382', ' 146', '2'], ['6491', '144', '352', ' 125', ' 382', ' 147', '2'], ['6494', '144', '354', ' 126', ' 383', ' 147', '2'], ['6497', '144', '355', ' 129', ' 384', ' 149', '2'], ['6498', '144', '353', ' 127', ' 387', ' 151', '2'], ['6499', '144', '353', ' 127', ' 388', ' 152', '2'], ['6500', '144', '353', ' 127', ' 388', ' 153', '2'], ['6501', '144', '353', ' 128', ' 389', ' 154', '2'], ['6503', '144', '354', ' 130', ' 387', ' 154', '2'], ['6504', '144', '354', ' 131', ' 387', ' 155', '2'], ['6505', '144', '354', ' 131', ' 388', ' 156', '2'], ['6506', '144', '353', ' 131', ' 390', ' 157', '2'], ['6507', '144', '353', ' 131', ' 390', ' 158', '2'], ['6508', '144', '353', ' 131', ' 391', ' 159', '2'], ['6509', '144', '354', ' 133', ' 391', ' 160', '2'], ['6510', '144', '354', ' 134', ' 393', ' 163', '2'], ['6511', '144', '355', ' 136', ' 395', ' 165', '2'], ['6512', '144', '355', ' 136', ' 397', ' 166', '2'], ['6513', '144', '355', ' 136', ' 397', ' 167', '2'], ['6514', '144', '355', ' 136', ' 399', ' 168', '2'], ['6515', '144', '354', ' 136', ' 399', ' 170', '2'], ['6516', '144', '353', ' 137', ' 399', ' 171', '2'], ['6517', '144', '353', ' 137', ' 399', ' 172', '2'], ['6518', '144', '354', ' 139', ' 399', ' 173', '2'], ['6519', '144', '355', ' 140', ' 399', ' 174', '2'], ['6520', '144', '355', ' 141', ' 399', ' 176', '2'], ['6521', '144', '355', ' 143', ' 400', ' 178', '2'], ['6522', '144', '355', ' 144', ' 401', ' 180', '2'], ['6523', '144', '355', ' 145', ' 401', ' 182', '2'], ['6524', '144', '355', ' 147', ' 401', ' 184', '2'], ['6525', '144', '355', ' 149', ' 401', ' 186', '2'], ['6526', '144', '355', ' 150', ' 402', ' 187', '2'], ['6527', '144', '357', ' 151', ' 403', ' 189', '2'], ['6528', '144', '357', ' 151', ' 405', ' 190', '2'], ['6529', '144', '358', ' 152', ' 405', ' 191', '2'], ['6530', '144', '359', ' 156', ' 406', ' 194', '2'], ['6531', '144', '357', ' 155', ' 408', ' 198', '2'], ['6532', '144', '357', ' 155', ' 410', ' 199', '2'], ['6533', '144', '357', ' 154', ' 412', ' 201', '2'], ['6534', '144', '359', ' 158', ' 413', ' 204', '2'], ['6535', '144', '360', ' 159', ' 414', ' 206', '2'], ['6536', '144', '361', ' 162', ' 415', ' 208', '2'], ['6537', '144', '362', ' 164', ' 416', ' 210', '2'], ['6538', '144', '362', ' 165', ' 418', ' 214', '2'], ['6539', '144', '362', ' 166', ' 420', ' 217', '2'], ['6540', '144', '361', ' 167', ' 422', ' 220', '2'], ['6541', '144', '362', ' 171', ' 422', ' 223', '2'], ['6542', '144', '363', ' 173', ' 423', ' 226', '2'], ['6543', '144', '364', ' 174', ' 425', ' 228', '2'], ['6544', '144', '365', ' 176', ' 427', ' 231', '2'], ['6545', '144', '366', ' 177', ' 430', ' 234', '2'], ['6546', '144', '367', ' 179', ' 432', ' 238', '2'], ['6547', '144', '367', ' 183', ' 434', ' 243', '2'], ['6548', '144', '367', ' 184', ' 436', ' 247', '2'], ['6549', '144', '367', ' 188', ' 438', ' 251', '2'], ['6550', '144', '370', ' 193', ' 440', ' 255', '2'], ['6551', '144', '369', ' 192', ' 444', ' 260', '2'], ['6552', '144', '370', ' 194', ' 447', ' 264', '2'], ['6553', '144', '371', ' 198', ' 450', ' 269', '2'], ['6554', '144', '372', ' 201', ' 454', ' 276', '2'], ['6555', '144', '373', ' 203', ' 457', ' 279', '2'], ['6556', '144', '374', ' 207', ' 461', ' 286', '2'], ['6557', '144', '375', ' 210', ' 464', ' 291', '2'], ['6558', '144', '377', ' 214', ' 468', ' 298', '2'], ['6559', '144', '379', ' 220', ' 473', ' 306', '2'], ['6560', '144', '380', ' 224', ' 476', ' 312', '2'], ['6561', '144', '381', ' 228', ' 480', ' 319', '2'], ['6562', '144', '383', ' 233', ' 485', ' 327', '2'], ['6563', '144', '384', ' 238', ' 491', ' 336', '2'], ['6564', '144', '387', ' 244', ' 497', ' 345', '2'], ['6565', '144', '389', ' 248', ' 504', ' 355', '2'], ['6566', '144', '391', ' 254', ' 511', ' 365', '2'], ['6567', '144', '393', ' 261', ' 519', ' 377', '2'], ['6568', '144', '396', ' 268', ' 526', ' 389', '2'], ['6569', '144', '396', ' 274', ' 536', ' 404', '2'], ['6570', '144', '401', ' 281', ' 542', ' 413', '2'], ['6571', '144', '409', ' 290', ' 546', ' 417', '2'], ['6572', '144', '419', ' 300', ' 551', ' 419', '2'], ['6573', '144', '430', ' 309', ' 554', ' 417', '2'], ['6575', '144', '445', ' 326', ' 556', ' 417', '2'], ['6576', '144', '457', ' 342', ' 554', ' 416', '2']]}, {'150': [['6659', '150', '379', ' 113', ' 404', ' 134', '2'], ['6661', '150', '380', ' 114', ' 405', ' 134', '2'], ['6663', '150', '380', ' 115', ' 406', ' 135', '2'], ['6664', '150', '379', ' 114', ' 407', ' 135', '2'], ['6665', '150', '379', ' 114', ' 408', ' 136', '2'], ['6666', '150', '380', ' 115', ' 409', ' 137', '2'], ['6667', '150', '380', ' 115', ' 409', ' 137', '2'], ['6668', '150', '381', ' 115', ' 409', ' 137', '2'], ['6669', '150', '381', ' 116', ' 409', ' 138', '2'], ['6670', '150', '381', ' 116', ' 410', ' 139', '2'], ['6671', '150', '382', ' 117', ' 410', ' 139', '2'], ['6672', '150', '382', ' 117', ' 411', ' 139', '2'], ['6673', '150', '383', ' 118', ' 411', ' 140', '2'], ['6676', '150', '385', ' 119', ' 413', ' 141', '2'], ['6677', '150', '385', ' 118', ' 414', ' 141', '2'], ['6678', '150', '383', ' 117', ' 415', ' 141', '2'], ['6679', '150', '384', ' 118', ' 415', ' 142', '2'], ['6680', '150', '384', ' 118', ' 416', ' 143', '2'], ['6681', '150', '385', ' 120', ' 416', ' 144', '2'], ['6682', '150', '387', ' 123', ' 416', ' 145', '2'], ['6684', '150', '389', ' 126', ' 416', ' 146', '2'], ['6685', '150', '389', ' 127', ' 416', ' 147', '2'], ['6686', '150', '389', ' 126', ' 417', ' 147', '2'], ['6693', '150', '391', ' 129', ' 423', ' 151', '2'], ['6694', '150', '390', ' 126', ' 424', ' 152', '2'], ['6695', '150', '390', ' 127', ' 425', ' 152', '2'], ['6696', '150', '390', ' 127', ' 426', ' 153', '2'], ['6697', '150', '391', ' 127', ' 427', ' 153', '2'], ['6698', '150', '391', ' 127', ' 428', ' 154', '2'], ['6699', '150', '392', ' 127', ' 429', ' 155', '2'], ['6700', '150', '393', ' 128', ' 429', ' 156', '2'], ['6702', '150', '393', ' 128', ' 431', ' 157', '2'], ['6703', '150', '393', ' 128', ' 432', ' 158', '2'], ['6704', '150', '393', ' 128', ' 433', ' 159', '2'], ['6705', '150', '394', ' 127', ' 435', ' 160', '2'], ['6706', '150', '395', ' 129', ' 436', ' 161', '2'], ['6707', '150', '396', ' 130', ' 437', ' 162', '2'], ['6708', '150', '397', ' 130', ' 439', ' 163', '2'], ['6709', '150', '397', ' 131', ' 439', ' 164', '2'], ['6710', '150', '397', ' 131', ' 440', ' 165', '2'], ['6711', '150', '398', ' 131', ' 441', ' 167', '2'], ['6712', '150', '398', ' 132', ' 442', ' 168', '2'], ['6713', '150', '398', ' 132', ' 444', ' 170', '2'], ['6714', '150', '398', ' 133', ' 444', ' 171', '2'], ['6715', '150', '400', ' 135', ' 444', ' 171', '2'], ['6716', '150', '400', ' 135', ' 444', ' 172', '2'], ['6717', '150', '403', ' 137', ' 445', ' 173', '2'], ['6718', '150', '404', ' 138', ' 446', ' 173', '2'], ['6719', '150', '404', ' 137', ' 448', ' 174', '2'], ['6720', '150', '405', ' 138', ' 448', ' 175', '2'], ['6721', '150', '405', ' 138', ' 451', ' 177', '2'], ['6722', '150', '406', ' 139', ' 451', ' 178', '2'], ['6723', '150', '407', ' 140', ' 454', ' 180', '2'], ['6724', '150', '408', ' 141', ' 456', ' 182', '2'], ['6725', '150', '409', ' 142', ' 457', ' 183', '2'], ['6726', '150', '410', ' 144', ' 457', ' 185', '2'], ['6727', '150', '411', ' 144', ' 459', ' 185', '2'], ['6728', '150', '412', ' 145', ' 460', ' 186', '2'], ['6729', '150', '413', ' 146', ' 462', ' 188', '2'], ['6730', '150', '414', ' 147', ' 463', ' 190', '2'], ['6731', '150', '414', ' 147', ' 464', ' 190', '2'], ['6732', '150', '416', ' 148', ' 466', ' 191', '2'], ['6733', '150', '416', ' 149', ' 467', ' 193', '2'], ['6734', '150', '418', ' 150', ' 469', ' 195', '2'], ['6735', '150', '418', ' 151', ' 471', ' 197', '2'], ['6736', '150', '418', ' 151', ' 472', ' 199', '2'], ['6737', '150', '421', ' 152', ' 473', ' 199', '2'], ['6738', '150', '422', ' 154', ' 475', ' 202', '2'], ['6739', '150', '423', ' 155', ' 478', ' 204', '2'], ['6740', '150', '425', ' 157', ' 479', ' 206', '2'], ['6741', '150', '426', ' 159', ' 481', ' 207', '2'], ['6742', '150', '426', ' 160', ' 483', ' 210', '2'], ['6743', '150', '427', ' 161', ' 485', ' 212', '2'], ['6744', '150', '428', ' 162', ' 487', ' 213', '2'], ['6745', '150', '429', ' 163', ' 490', ' 217', '2'], ['6746', '150', '431', ' 164', ' 493', ' 219', '2'], ['6747', '150', '432', ' 165', ' 494', ' 220', '2'], ['6748', '150', '433', ' 166', ' 496', ' 222', '2'], ['6749', '150', '434', ' 167', ' 498', ' 224', '2'], ['6750', '150', '435', ' 168', ' 501', ' 227', '2'], ['6751', '150', '437', ' 169', ' 504', ' 229', '2'], ['6752', '150', '438', ' 171', ' 507', ' 232', '2'], ['6753', '150', '441', ' 173', ' 510', ' 236', '2'], ['6754', '150', '443', ' 175', ' 512', ' 237', '2'], ['6755', '150', '445', ' 177', ' 516', ' 240', '2'], ['6756', '150', '446', ' 178', ' 520', ' 245', '2'], ['6757', '150', '448', ' 182', ' 522', ' 249', '2'], ['6758', '150', '450', ' 183', ' 526', ' 252', '2'], ['6759', '150', '451', ' 184', ' 529', ' 255', '2'], ['6760', '150', '455', ' 190', ' 531', ' 258', '2'], ['6761', '150', '457', ' 192', ' 535', ' 262', '2'], ['6762', '150', '459', ' 192', ' 540', ' 265', '2'], ['6763', '150', '459', ' 193', ' 545', ' 270', '2'], ['6764', '150', '462', ' 195', ' 551', ' 276', '2'], ['6765', '150', '464', ' 197', ' 554', ' 279', '2'], ['6766', '150', '467', ' 198', ' 556', ' 279', '2'], ['6767', '150', '469', ' 200', ' 562', ' 285', '2'], ['6768', '150', '472', ' 203', ' 567', ' 289', '2'], ['6769', '150', '474', ' 204', ' 571', ' 292', '2'], ['6770', '150', '478', ' 209', ' 577', ' 299', '2'], ['6771', '150', '481', ' 213', ' 583', ' 306', '2'], ['6773', '150', '487', ' 219', ' 592', ' 315', '2'], ['6774', '150', '491', ' 222', ' 600', ' 322', '2'], ['6775', '150', '494', ' 225', ' 607', ' 329', '2'], ['6777', '150', '499', ' 232', ' 619', ' 342', '2'], ['6778', '150', '506', ' 238', ' 627', ' 348', '2'], ['6779', '150', '511', ' 241', ' 637', ' 356', '2'], ['6780', '150', '514', ' 245', ' 645', ' 365', '2'], ['6781', '150', '520', ' 250', ' 655', ' 373', '2'], ['6782', '150', '524', ' 253', ' 664', ' 382', '2'], ['6783', '150', '528', ' 258', ' 675', ' 393', '2'], ['6784', '150', '533', ' 264', ' 685', ' 405', '2'], ['6785', '150', '540', ' 269', ' 695', ' 412', '2'], ['6786', '150', '549', ' 275', ' 703', ' 417', '2'], ['6787', '150', '560', ' 280', ' 712', ' 418', '2'], ['6788', '150', '571', ' 288', ' 719', ' 419', '2'], ['6789', '150', '580', ' 295', ' 722', ' 417', '2'], ['6790', '150', '589', ' 302', ' 724', ' 414', '2'], ['6791', '150', '599', ' 310', ' 731', ' 417', '2'], ['6792', '150', '610', ' 317', ' 738', ' 417', '2'], ['6793', '150', '620', ' 325', ' 744', ' 417', '2'], ['6794', '150', '631', ' 335', ' 748', ' 417', '2'], ['6795', '150', '641', ' 344', ' 748', ' 415', '2']]}, {'157': [['7589', '157', '379', ' 101', ' 400', ' 119', '2'], ['7590', '157', '379', ' 100', ' 400', ' 118', '2'], ['7591', '157', '380', ' 101', ' 400', ' 119', '2'], ['7592', '157', '380', ' 102', ' 400', ' 119', '2'], ['7593', '157', '380', ' 102', ' 400', ' 119', '2'], ['7594', '157', '380', ' 102', ' 400', ' 119', '2'], ['7595', '157', '380', ' 102', ' 400', ' 119', '2'], ['7596', '157', '380', ' 102', ' 400', ' 118', '2'], ['7597', '157', '380', ' 103', ' 399', ' 119', '2'], ['7602', '157', '380', ' 103', ' 399', ' 119', '2'], ['7604', '157', '379', ' 104', ' 398', ' 119', '2'], ['7605', '157', '379', ' 104', ' 398', ' 120', '2'], ['7606', '157', '379', ' 104', ' 398', ' 120', '2'], ['7615', '157', '378', ' 105', ' 399', ' 121', '2'], ['7616', '157', '378', ' 105', ' 399', ' 122', '2'], ['7617', '157', '379', ' 105', ' 399', ' 122', '2'], ['7618', '157', '379', ' 105', ' 399', ' 122', '2'], ['7619', '157', '379', ' 106', ' 399', ' 122', '2'], ['7620', '157', '379', ' 106', ' 399', ' 122', '2'], ['7621', '157', '380', ' 106', ' 400', ' 122', '2'], ['7622', '157', '379', ' 106', ' 400', ' 122', '2'], ['7623', '157', '379', ' 105', ' 400', ' 122', '2'], ['7624', '157', '379', ' 105', ' 401', ' 122', '2'], ['7625', '157', '379', ' 105', ' 401', ' 122', '2'], ['7626', '157', '380', ' 105', ' 400', ' 122', '2'], ['7627', '157', '380', ' 105', ' 400', ' 122', '2'], ['7628', '157', '380', ' 106', ' 401', ' 122', '2'], ['7629', '157', '379', ' 106', ' 401', ' 122', '2'], ['7630', '157', '379', ' 106', ' 401', ' 123', '2'], ['7631', '157', '379', ' 106', ' 401', ' 123', '2'], ['7643', '157', '381', ' 108', ' 402', ' 125', '2'], ['7644', '157', '380', ' 108', ' 403', ' 126', '2'], ['7645', '157', '380', ' 108', ' 404', ' 126', '2'], ['7646', '157', '380', ' 108', ' 405', ' 127', '2'], ['7647', '157', '380', ' 108', ' 405', ' 127', '2'], ['7648', '157', '381', ' 109', ' 405', ' 128', '2'], ['7649', '157', '381', ' 109', ' 406', ' 128', '2'], ['7650', '157', '382', ' 110', ' 405', ' 129', '2'], ['7651', '157', '382', ' 110', ' 405', ' 128', '2'], ['7652', '157', '382', ' 111', ' 405', ' 128', '2'], ['7653', '157', '382', ' 111', ' 404', ' 128', '2'], ['7654', '157', '381', ' 111', ' 405', ' 128', '2'], ['7655', '157', '382', ' 111', ' 404', ' 128', '2'], ['7656', '157', '381', ' 111', ' 405', ' 128', '2'], ['7657', '157', '382', ' 111', ' 405', ' 128', '2'], ['7658', '157', '382', ' 111', ' 405', ' 129', '2'], ['7659', '157', '382', ' 111', ' 405', ' 129', '2'], ['7660', '157', '383', ' 111', ' 406', ' 129', '2'], ['7661', '157', '383', ' 112', ' 406', ' 129', '2'], ['7662', '157', '383', ' 112', ' 406', ' 129', '2'], ['7663', '157', '382', ' 111', ' 407', ' 130', '2'], ['7664', '157', '383', ' 111', ' 408', ' 130', '2'], ['7665', '157', '384', ' 111', ' 408', ' 130', '2'], ['7666', '157', '384', ' 111', ' 408', ' 130', '2'], ['7667', '157', '384', ' 112', ' 408', ' 130', '2'], ['7668', '157', '384', ' 112', ' 408', ' 130', '2'], ['7669', '157', '384', ' 112', ' 408', ' 130', '2'], ['7670', '157', '384', ' 113', ' 408', ' 131', '2'], ['7671', '157', '384', ' 113', ' 409', ' 131', '2'], ['7672', '157', '383', ' 113', ' 409', ' 131', '2'], ['7673', '157', '384', ' 113', ' 408', ' 132', '2'], ['7674', '157', '383', ' 113', ' 409', ' 132', '2'], ['7675', '157', '384', ' 114', ' 409', ' 132', '2'], ['7676', '157', '383', ' 114', ' 410', ' 133', '2'], ['7677', '157', '383', ' 114', ' 410', ' 134', '2'], ['7678', '157', '383', ' 114', ' 410', ' 134', '2'], ['7679', '157', '384', ' 114', ' 410', ' 134', '2'], ['7680', '157', '385', ' 115', ' 410', ' 134', '2'], ['7681', '157', '385', ' 115', ' 410', ' 134', '2'], ['7682', '157', '385', ' 116', ' 410', ' 134', '2'], ['7683', '157', '385', ' 115', ' 411', ' 134', '2'], ['7684', '157', '386', ' 115', ' 411', ' 135', '2'], ['7685', '157', '386', ' 116', ' 411', ' 135', '2'], ['7686', '157', '386', ' 115', ' 412', ' 135', '2'], ['7687', '157', '385', ' 115', ' 412', ' 136', '2'], ['7688', '157', '385', ' 115', ' 412', ' 136', '2'], ['7689', '157', '385', ' 115', ' 413', ' 137', '2'], ['7690', '157', '385', ' 115', ' 413', ' 137', '2'], ['7691', '157', '385', ' 115', ' 413', ' 138', '2'], ['7692', '157', '385', ' 115', ' 414', ' 138', '2'], ['7693', '157', '385', ' 115', ' 414', ' 139', '2'], ['7694', '157', '386', ' 115', ' 414', ' 139', '2'], ['7695', '157', '386', ' 115', ' 414', ' 139', '2'], ['7696', '157', '387', ' 116', ' 414', ' 140', '2'], ['7697', '157', '387', ' 116', ' 414', ' 140', '2'], ['7698', '157', '387', ' 117', ' 414', ' 140', '2'], ['7699', '157', '388', ' 117', ' 415', ' 140', '2'], ['7700', '157', '389', ' 118', ' 415', ' 140', '2'], ['7701', '157', '389', ' 119', ' 415', ' 141', '2'], ['7702', '157', '390', ' 120', ' 416', ' 141', '2'], ['7703', '157', '390', ' 121', ' 416', ' 142', '2'], ['7704', '157', '389', ' 119', ' 417', ' 142', '2'], ['7705', '157', '389', ' 120', ' 417', ' 142', '2'], ['7706', '157', '390', ' 120', ' 418', ' 143', '2'], ['7707', '157', '390', ' 120', ' 419', ' 143', '2'], ['7708', '157', '390', ' 121', ' 419', ' 144', '2'], ['7709', '157', '390', ' 121', ' 420', ' 145', '2'], ['7710', '157', '390', ' 121', ' 420', ' 145', '2'], ['7711', '157', '390', ' 121', ' 420', ' 145', '2'], ['7712', '157', '390', ' 121', ' 420', ' 146', '2'], ['7713', '157', '390', ' 122', ' 420', ' 147', '2'], ['7714', '157', '391', ' 123', ' 421', ' 147', '2'], ['7715', '157', '392', ' 124', ' 421', ' 147', '2'], ['7716', '157', '393', ' 124', ' 421', ' 147', '2'], ['7717', '157', '393', ' 125', ' 421', ' 147', '2'], ['7718', '157', '394', ' 126', ' 422', ' 148', '2'], ['7719', '157', '394', ' 127', ' 422', ' 149', '2'], ['7720', '157', '393', ' 128', ' 423', ' 150', '2'], ['7721', '157', '394', ' 128', ' 424', ' 151', '2'], ['7722', '157', '394', ' 128', ' 424', ' 151', '2'], ['7723', '157', '394', ' 128', ' 425', ' 151', '2'], ['7724', '157', '395', ' 128', ' 426', ' 152', '2'], ['7725', '157', '396', ' 129', ' 426', ' 152', '2'], ['7726', '157', '396', ' 130', ' 426', ' 152', '2'], ['7727', '157', '396', ' 130', ' 426', ' 153', '2'], ['7728', '157', '396', ' 130', ' 427', ' 153', '2'], ['7729', '157', '397', ' 130', ' 428', ' 153', '2'], ['7730', '157', '397', ' 131', ' 429', ' 154', '2'], ['7731', '157', '397', ' 131', ' 430', ' 155', '2'], ['7732', '157', '398', ' 131', ' 431', ' 156', '2'], ['7733', '157', '398', ' 132', ' 432', ' 157', '2'], ['7734', '157', '398', ' 132', ' 434', ' 158', '2'], ['7735', '157', '399', ' 132', ' 434', ' 159', '2'], ['7736', '157', '399', ' 133', ' 434', ' 159', '2'], ['7737', '157', '399', ' 134', ' 434', ' 160', '2'], ['7738', '157', '399', ' 134', ' 434', ' 160', '2'], ['7739', '157', '400', ' 134', ' 435', ' 160', '2'], ['7740', '157', '401', ' 135', ' 436', ' 161', '2'], ['7741', '157', '400', ' 135', ' 437', ' 162', '2'], ['7742', '157', '400', ' 134', ' 439', ' 163', '2'], ['7743', '157', '400', ' 134', ' 439', ' 164', '2'], ['7744', '157', '401', ' 135', ' 439', ' 164', '2'], ['7745', '157', '401', ' 135', ' 441', ' 165', '2'], ['7746', '157', '402', ' 135', ' 442', ' 166', '2'], ['7747', '157', '402', ' 136', ' 441', ' 166', '2'], ['7748', '157', '404', ' 138', ' 442', ' 166', '2'], ['7749', '157', '405', ' 138', ' 443', ' 167', '2'], ['7750', '157', '405', ' 139', ' 445', ' 169', '2'], ['7751', '157', '406', ' 139', ' 446', ' 170', '2'], ['7752', '157', '407', ' 140', ' 447', ' 170', '2'], ['7753', '157', '407', ' 140', ' 448', ' 171', '2'], ['7754', '157', '408', ' 142', ' 448', ' 172', '2'], ['7755', '157', '408', ' 142', ' 449', ' 173', '2'], ['7756', '157', '408', ' 142', ' 450', ' 175', '2'], ['7757', '157', '408', ' 142', ' 451', ' 176', '2'], ['7758', '157', '410', ' 143', ' 452', ' 176', '2'], ['7759', '157', '411', ' 145', ' 451', ' 176', '2'], ['7760', '157', '411', ' 145', ' 452', ' 177', '2'], ['7761', '157', '412', ' 146', ' 454', ' 178', '2'], ['7762', '157', '412', ' 146', ' 455', ' 179', '2'], ['7763', '157', '413', ' 147', ' 455', ' 180', '2'], ['7764', '157', '413', ' 148', ' 456', ' 181', '2'], ['7765', '157', '414', ' 149', ' 457', ' 182', '2'], ['7766', '157', '415', ' 149', ' 459', ' 184', '2'], ['7767', '157', '415', ' 150', ' 461', ' 185', '2'], ['7768', '157', '415', ' 149', ' 462', ' 186', '2'], ['7769', '157', '415', ' 149', ' 463', ' 187', '2'], ['7770', '157', '416', ' 150', ' 464', ' 188', '2'], ['7771', '157', '418', ' 151', ' 465', ' 189', '2'], ['7772', '157', '419', ' 152', ' 466', ' 190', '2'], ['7773', '157', '420', ' 152', ' 467', ' 190', '2'], ['7774', '157', '420', ' 153', ' 469', ' 193', '2'], ['7775', '157', '421', ' 154', ' 470', ' 194', '2'], ['7776', '157', '421', ' 155', ' 471', ' 195', '2'], ['7777', '157', '423', ' 157', ' 472', ' 197', '2'], ['7778', '157', '424', ' 158', ' 474', ' 199', '2'], ['7779', '157', '424', ' 158', ' 475', ' 201', '2'], ['7780', '157', '425', ' 159', ' 476', ' 202', '2'], ['7781', '157', '426', ' 160', ' 478', ' 203', '2'], ['7782', '157', '427', ' 161', ' 479', ' 204', '2'], ['7783', '157', '428', ' 162', ' 480', ' 205', '2'], ['7784', '157', '429', ' 163', ' 482', ' 207', '2'], ['7785', '157', '430', ' 165', ' 483', ' 209', '2'], ['7786', '157', '432', ' 166', ' 485', ' 211', '2'], ['7787', '157', '432', ' 167', ' 486', ' 213', '2'], ['7788', '157', '433', ' 168', ' 488', ' 215', '2'], ['7789', '157', '434', ' 169', ' 489', ' 216', '2'], ['7790', '157', '435', ' 170', ' 491', ' 217', '2'], ['7791', '157', '435', ' 171', ' 493', ' 220', '2'], ['7792', '157', '436', ' 173', ' 496', ' 224', '2'], ['7793', '157', '437', ' 174', ' 498', ' 226', '2'], ['7794', '157', '439', ' 177', ' 498', ' 228', '2'], ['7795', '157', '441', ' 179', ' 499', ' 228', '2'], ['7796', '157', '442', ' 181', ' 501', ' 230', '2'], ['7797', '157', '444', ' 183', ' 505', ' 234', '2'], ['7798', '157', '446', ' 184', ' 509', ' 237', '2'], ['7799', '157', '446', ' 186', ' 510', ' 239', '2'], ['7800', '157', '447', ' 187', ' 511', ' 241', '2'], ['7801', '157', '448', ' 190', ' 513', ' 243', '2'], ['7802', '157', '450', ' 192', ' 518', ' 248', '2'], ['7803', '157', '451', ' 192', ' 523', ' 251', '2'], ['7804', '157', '453', ' 194', ' 525', ' 254', '2'], ['7805', '157', '455', ' 197', ' 526', ' 256', '2'], ['7806', '157', '457', ' 198', ' 530', ' 258', '2'], ['7807', '157', '457', ' 199', ' 533', ' 262', '2'], ['7808', '157', '459', ' 202', ' 535', ' 265', '2'], ['7809', '157', '461', ' 204', ' 537', ' 266', '2'], ['7810', '157', '462', ' 205', ' 541', ' 270', '2'], ['7811', '157', '466', ' 209', ' 546', ' 274', '2'], ['7812', '157', '469', ' 212', ' 549', ' 277', '2'], ['7813', '157', '470', ' 215', ' 553', ' 282', '2'], ['7814', '157', '472', ' 218', ' 558', ' 287', '2'], ['7815', '157', '474', ' 219', ' 562', ' 291', '2'], ['7816', '157', '476', ' 222', ' 567', ' 295', '2'], ['7817', '157', '479', ' 224', ' 572', ' 300', '2'], ['7818', '157', '482', ' 229', ' 576', ' 304', '2'], ['7819', '157', '485', ' 231', ' 581', ' 308', '2'], ['7820', '157', '487', ' 235', ' 587', ' 315', '2'], ['7821', '157', '491', ' 239', ' 593', ' 321', '2'], ['7822', '157', '494', ' 243', ' 599', ' 327', '2'], ['7823', '157', '498', ' 248', ' 604', ' 332', '2'], ['7824', '157', '502', ' 251', ' 612', ' 338', '2'], ['7825', '157', '504', ' 254', ' 618', ' 345', '2'], ['7826', '157', '510', ' 259', ' 626', ' 352', '2'], ['7827', '157', '513', ' 263', ' 634', ' 359', '2'], ['7828', '157', '517', ' 269', ' 642', ' 368', '2'], ['7829', '157', '522', ' 274', ' 651', ' 376', '2'], ['7830', '157', '525', ' 278', ' 660', ' 385', '2'], ['7831', '157', '529', ' 284', ' 669', ' 396', '2'], ['7832', '157', '533', ' 290', ' 679', ' 407', '2'], ['7833', '157', '541', ' 296', ' 688', ' 412', '2'], ['7834', '157', '551', ' 302', ' 696', ' 415', '2'], ['7835', '157', '564', ' 310', ' 702', ' 416', '2'], ['7836', '157', '572', ' 317', ' 708', ' 418', '2'], ['7837', '157', '582', ' 323', ' 713', ' 417', '2'], ['7838', '157', '592', ' 328', ' 718', ' 416', '2'], ['7839', '157', '605', ' 338', ' 724', ' 416', '2'], ['7840', '157', '615', ' 346', ' 728', ' 417', '2'], ['7841', '157', '628', ' 357', ' 730', ' 416', '2']]}, {'180': [['8642', '180', '337', ' 106', ' 361', ' 124', '2'], ['8680', '180', '341', ' 120', ' 369', ' 141', '2'], ['8685', '180', '340', ' 118', ' 372', ' 143', '2'], ['8688', '180', '339', ' 117', ' 374', ' 145', '2'], ['8697', '180', '340', ' 123', ' 374', ' 149', '2'], ['8698', '180', '340', ' 124', ' 375', ' 152', '2'], ['8699', '180', '340', ' 125', ' 375', ' 153', '2'], ['8701', '180', '339', ' 126', ' 374', ' 154', '2'], ['8702', '180', '339', ' 127', ' 374', ' 154', '2'], ['8703', '180', '341', ' 128', ' 374', ' 154', '2'], ['8704', '180', '340', ' 128', ' 374', ' 155', '2'], ['8705', '180', '340', ' 128', ' 374', ' 155', '2'], ['8706', '180', '339', ' 129', ' 374', ' 156', '2'], ['8707', '180', '339', ' 129', ' 374', ' 157', '2'], ['8708', '180', '340', ' 130', ' 376', ' 158', '2'], ['8709', '180', '339', ' 130', ' 376', ' 159', '2'], ['8710', '180', '339', ' 130', ' 377', ' 160', '2'], ['8711', '180', '339', ' 130', ' 377', ' 161', '2'], ['8712', '180', '339', ' 131', ' 376', ' 161', '2'], ['8713', '180', '339', ' 131', ' 378', ' 163', '2'], ['8714', '180', '341', ' 131', ' 382', ' 165', '2'], ['8715', '180', '340', ' 131', ' 380', ' 165', '2'], ['8716', '180', '339', ' 132', ' 380', ' 166', '2'], ['8717', '180', '339', ' 133', ' 379', ' 167', '2'], ['8718', '180', '341', ' 134', ' 384', ' 170', '2'], ['8719', '180', '342', ' 135', ' 387', ' 171', '2'], ['8720', '180', '343', ' 135', ' 388', ' 172', '2'], ['8721', '180', '340', ' 135', ' 385', ' 172', '2'], ['8722', '180', '340', ' 135', ' 386', ' 173', '2'], ['8723', '180', '339', ' 135', ' 387', ' 175', '2'], ['8724', '180', '338', ' 135', ' 386', ' 176', '2'], ['8727', '180', '337', ' 138', ' 386', ' 180', '2'], ['8729', '180', '337', ' 140', ' 386', ' 182', '2'], ['8730', '180', '339', ' 143', ' 384', ' 184', '2'], ['8733', '180', '339', ' 145', ' 385', ' 186', '2'], ['8734', '180', '339', ' 146', ' 386', ' 188', '2'], ['8735', '180', '341', ' 147', ' 386', ' 188', '2'], ['8736', '180', '340', ' 147', ' 387', ' 191', '2'], ['8737', '180', '340', ' 147', ' 387', ' 193', '2'], ['8738', '180', '339', ' 150', ' 387', ' 195', '2'], ['8739', '180', '340', ' 153', ' 386', ' 197', '2'], ['8740', '180', '341', ' 153', ' 387', ' 198', '2'], ['8741', '180', '341', ' 154', ' 388', ' 200', '2'], ['8742', '180', '341', ' 154', ' 389', ' 203', '2'], ['8743', '180', '343', ' 158', ' 389', ' 204', '2'], ['8744', '180', '342', ' 157', ' 391', ' 207', '2'], ['8745', '180', '342', ' 158', ' 392', ' 209', '2'], ['8746', '180', '342', ' 158', ' 392', ' 210', '2'], ['8747', '180', '342', ' 160', ' 393', ' 213', '2'], ['8748', '180', '343', ' 161', ' 393', ' 215', '2'], ['8749', '180', '342', ' 162', ' 394', ' 217', '2'], ['8750', '180', '342', ' 164', ' 394', ' 220', '2'], ['8751', '180', '342', ' 165', ' 395', ' 223', '2'], ['8752', '180', '342', ' 165', ' 396', ' 225', '2'], ['8753', '180', '341', ' 166', ' 397', ' 228', '2'], ['8754', '180', '341', ' 167', ' 398', ' 230', '2'], ['8755', '180', '342', ' 168', ' 399', ' 232', '2'], ['8756', '180', '343', ' 171', ' 399', ' 234', '2'], ['8757', '180', '343', ' 173', ' 400', ' 237', '2'], ['8758', '180', '344', ' 175', ' 402', ' 240', '2'], ['8759', '180', '343', ' 177', ' 404', ' 245', '2'], ['8760', '180', '343', ' 178', ' 406', ' 249', '2'], ['8761', '180', '343', ' 182', ' 407', ' 253', '2'], ['8762', '180', '343', ' 184', ' 409', ' 257', '2'], ['8763', '180', '342', ' 185', ' 411', ' 261', '2'], ['8764', '180', '344', ' 190', ' 410', ' 265', '2'], ['8765', '180', '342', ' 191', ' 412', ' 269', '2'], ['8766', '180', '343', ' 196', ' 413', ' 274', '2'], ['8767', '180', '342', ' 196', ' 415', ' 277', '2'], ['8768', '180', '343', ' 198', ' 417', ' 281', '2'], ['8769', '180', '342', ' 200', ' 418', ' 284', '2'], ['8770', '180', '343', ' 203', ' 421', ' 290', '2'], ['8771', '180', '343', ' 205', ' 425', ' 297', '2'], ['8772', '180', '343', ' 208', ' 426', ' 300', '2'], ['8773', '180', '342', ' 212', ' 427', ' 307', '2'], ['8774', '180', '343', ' 216', ' 429', ' 312', '2'], ['8775', '180', '344', ' 219', ' 434', ' 319', '2'], ['8776', '180', '344', ' 223', ' 436', ' 324', '2'], ['8777', '180', '344', ' 226', ' 438', ' 329', '2'], ['8778', '180', '345', ' 230', ' 441', ' 336', '2'], ['8779', '180', '343', ' 233', ' 445', ' 347', '2'], ['8780', '180', '344', ' 238', ' 448', ' 354', '2'], ['8781', '180', '343', ' 242', ' 450', ' 361', '2'], ['8782', '180', '342', ' 247', ' 454', ' 372', '2'], ['8783', '180', '341', ' 252', ' 458', ' 381', '2'], ['8784', '180', '340', ' 257', ' 463', ' 395', '2'], ['8785', '180', '341', ' 263', ' 468', ' 406', '2'], ['8786', '180', '342', ' 268', ' 471', ' 412', '2'], ['8787', '180', '345', ' 273', ' 473', ' 415', '2'], ['8788', '180', '349', ' 280', ' 474', ' 417', '2'], ['8789', '180', '355', ' 287', ' 476', ' 417', '2'], ['8794', '180', '372', ' 314', ' 471', ' 415', '2'], ['8795', '180', '383', ' 336', ' 468', ' 416', '2']]}, {'186': [['8931', '186', '370', ' 107', ' 392', ' 121', '2'], ['8932', '186', '370', ' 108', ' 392', ' 122', '2'], ['8933', '186', '369', ' 108', ' 392', ' 122', '2'], ['8934', '186', '368', ' 108', ' 393', ' 123', '2'], ['8935', '186', '369', ' 108', ' 393', ' 124', '2'], ['8936', '186', '370', ' 109', ' 393', ' 124', '2'], ['8937', '186', '372', ' 110', ' 393', ' 124', '2'], ['8938', '186', '372', ' 111', ' 394', ' 124', '2'], ['8939', '186', '373', ' 111', ' 395', ' 125', '2'], ['8940', '186', '372', ' 111', ' 395', ' 125', '2'], ['8941', '186', '372', ' 111', ' 396', ' 126', '2'], ['8942', '186', '372', ' 110', ' 397', ' 126', '2'], ['8943', '186', '372', ' 110', ' 397', ' 126', '2'], ['8944', '186', '372', ' 109', ' 398', ' 126', '2'], ['8945', '186', '372', ' 109', ' 398', ' 126', '2'], ['8946', '186', '372', ' 109', ' 399', ' 126', '2'], ['8947', '186', '373', ' 109', ' 400', ' 127', '2'], ['8948', '186', '373', ' 109', ' 400', ' 127', '2'], ['8949', '186', '374', ' 110', ' 400', ' 127', '2'], ['8950', '186', '374', ' 109', ' 400', ' 127', '2'], ['8951', '186', '374', ' 110', ' 401', ' 128', '2'], ['8952', '186', '374', ' 109', ' 401', ' 127', '2'], ['8953', '186', '374', ' 109', ' 401', ' 127', '2'], ['8954', '186', '375', ' 109', ' 401', ' 127', '2'], ['8955', '186', '375', ' 109', ' 401', ' 127', '2'], ['8956', '186', '375', ' 110', ' 401', ' 128', '2'], ['8957', '186', '375', ' 110', ' 402', ' 128', '2'], ['8958', '186', '375', ' 110', ' 402', ' 129', '2'], ['8959', '186', '375', ' 110', ' 403', ' 129', '2'], ['8960', '186', '377', ' 112', ' 403', ' 130', '2'], ['8961', '186', '377', ' 113', ' 403', ' 131', '2'], ['8962', '186', '377', ' 112', ' 404', ' 131', '2'], ['8963', '186', '377', ' 112', ' 405', ' 132', '2'], ['8964', '186', '378', ' 112', ' 405', ' 132', '2'], ['8965', '186', '378', ' 113', ' 405', ' 132', '2'], ['8966', '186', '378', ' 113', ' 406', ' 132', '2'], ['8967', '186', '379', ' 113', ' 406', ' 133', '2'], ['8968', '186', '379', ' 113', ' 406', ' 133', '2'], ['8969', '186', '379', ' 113', ' 407', ' 133', '2'], ['8970', '186', '379', ' 113', ' 407', ' 133', '2'], ['8971', '186', '379', ' 113', ' 407', ' 133', '2'], ['8972', '186', '380', ' 114', ' 407', ' 133', '2'], ['8973', '186', '380', ' 114', ' 408', ' 134', '2'], ['8974', '186', '380', ' 114', ' 408', ' 134', '2'], ['8975', '186', '380', ' 113', ' 408', ' 135', '2'], ['8976', '186', '381', ' 113', ' 409', ' 135', '2'], ['8977', '186', '381', ' 113', ' 409', ' 135', '2'], ['8978', '186', '381', ' 113', ' 409', ' 135', '2'], ['8979', '186', '381', ' 113', ' 410', ' 135', '2'], ['8980', '186', '381', ' 114', ' 410', ' 136', '2'], ['8981', '186', '381', ' 114', ' 410', ' 136', '2'], ['8982', '186', '382', ' 116', ' 410', ' 137', '2'], ['8983', '186', '382', ' 116', ' 411', ' 137', '2'], ['8984', '186', '383', ' 116', ' 411', ' 138', '2'], ['8985', '186', '383', ' 116', ' 412', ' 138', '2'], ['8986', '186', '384', ' 116', ' 412', ' 138', '2'], ['8987', '186', '384', ' 117', ' 413', ' 139', '2'], ['8988', '186', '385', ' 117', ' 414', ' 139', '2'], ['8989', '186', '386', ' 117', ' 415', ' 139', '2'], ['8990', '186', '386', ' 118', ' 415', ' 140', '2'], ['8991', '186', '387', ' 118', ' 416', ' 140', '2'], ['8992', '186', '388', ' 119', ' 416', ' 141', '2'], ['8993', '186', '389', ' 119', ' 416', ' 141', '2'], ['8994', '186', '389', ' 120', ' 416', ' 141', '2'], ['8995', '186', '389', ' 121', ' 417', ' 142', '2'], ['8996', '186', '389', ' 121', ' 418', ' 143', '2'], ['8997', '186', '389', ' 121', ' 419', ' 144', '2'], ['8998', '186', '389', ' 122', ' 419', ' 145', '2'], ['8999', '186', '389', ' 122', ' 420', ' 146', '2'], ['9000', '186', '390', ' 122', ' 420', ' 146', '2'], ['9001', '186', '390', ' 123', ' 421', ' 146', '2'], ['9002', '186', '390', ' 122', ' 422', ' 147', '2'], ['9003', '186', '390', ' 122', ' 422', ' 147', '2'], ['9004', '186', '392', ' 123', ' 423', ' 147', '2'], ['9005', '186', '393', ' 124', ' 423', ' 147', '2'], ['9006', '186', '393', ' 125', ' 423', ' 148', '2'], ['9007', '186', '394', ' 126', ' 423', ' 148', '2'], ['9008', '186', '394', ' 127', ' 424', ' 149', '2'], ['9009', '186', '395', ' 127', ' 425', ' 150', '2'], ['9010', '186', '395', ' 127', ' 427', ' 151', '2'], ['9011', '186', '395', ' 127', ' 428', ' 151', '2'], ['9012', '186', '395', ' 128', ' 428', ' 152', '2'], ['9013', '186', '396', ' 129', ' 427', ' 152', '2'], ['9014', '186', '397', ' 130', ' 428', ' 152', '2'], ['9015', '186', '397', ' 130', ' 429', ' 153', '2'], ['9016', '186', '397', ' 130', ' 430', ' 154', '2'], ['9017', '186', '398', ' 130', ' 432', ' 155', '2'], ['9018', '186', '398', ' 130', ' 433', ' 155', '2'], ['9019', '186', '398', ' 130', ' 435', ' 157', '2'], ['9020', '186', '398', ' 131', ' 435', ' 157', '2'], ['9021', '186', '399', ' 131', ' 435', ' 158', '2'], ['9022', '186', '399', ' 132', ' 436', ' 158', '2'], ['9023', '186', '400', ' 132', ' 436', ' 158', '2'], ['9024', '186', '400', ' 132', ' 437', ' 159', '2'], ['9025', '186', '401', ' 133', ' 437', ' 159', '2'], ['9026', '186', '401', ' 134', ' 437', ' 160', '2'], ['9027', '186', '401', ' 133', ' 439', ' 160', '2'], ['9028', '186', '402', ' 134', ' 439', ' 161', '2'], ['9029', '186', '403', ' 134', ' 441', ' 162', '2'], ['9030', '186', '404', ' 135', ' 443', ' 163', '2'], ['9031', '186', '404', ' 136', ' 444', ' 164', '2'], ['9032', '186', '404', ' 136', ' 444', ' 165', '2'], ['9033', '186', '406', ' 137', ' 445', ' 165', '2'], ['9034', '186', '406', ' 138', ' 446', ' 166', '2'], ['9035', '186', '406', ' 138', ' 447', ' 167', '2'], ['9036', '186', '407', ' 139', ' 449', ' 168', '2'], ['9037', '186', '408', ' 139', ' 450', ' 169', '2'], ['9038', '186', '408', ' 140', ' 450', ' 170', '2'], ['9039', '186', '409', ' 141', ' 451', ' 171', '2'], ['9040', '186', '409', ' 141', ' 452', ' 172', '2'], ['9041', '186', '410', ' 141', ' 452', ' 172', '2'], ['9042', '186', '411', ' 142', ' 452', ' 172', '2'], ['9043', '186', '412', ' 143', ' 453', ' 173', '2'], ['9044', '186', '412', ' 144', ' 454', ' 174', '2'], ['9045', '186', '413', ' 144', ' 456', ' 176', '2'], ['9046', '186', '415', ' 145', ' 458', ' 177', '2'], ['9047', '186', '416', ' 146', ' 459', ' 178', '2'], ['9048', '186', '416', ' 146', ' 460', ' 179', '2'], ['9049', '186', '416', ' 146', ' 461', ' 180', '2'], ['9050', '186', '416', ' 147', ' 462', ' 181', '2'], ['9051', '186', '417', ' 148', ' 463', ' 183', '2'], ['9052', '186', '418', ' 149', ' 464', ' 184', '2'], ['9053', '186', '418', ' 149', ' 465', ' 184', '2'], ['9054', '186', '419', ' 149', ' 466', ' 185', '2'], ['9055', '186', '421', ' 152', ' 465', ' 185', '2'], ['9056', '186', '420', ' 152', ' 466', ' 187', '2'], ['9057', '186', '420', ' 152', ' 468', ' 189', '2'], ['9058', '186', '422', ' 153', ' 469', ' 190', '2'], ['9059', '186', '424', ' 156', ' 469', ' 191', '2'], ['9060', '186', '423', ' 156', ' 470', ' 192', '2'], ['9061', '186', '424', ' 157', ' 472', ' 195', '2'], ['9062', '186', '425', ' 157', ' 474', ' 196', '2'], ['9063', '186', '427', ' 159', ' 475', ' 197', '2'], ['9064', '186', '427', ' 159', ' 478', ' 199', '2'], ['9065', '186', '427', ' 159', ' 479', ' 200', '2'], ['9066', '186', '429', ' 160', ' 481', ' 202', '2'], ['9067', '186', '429', ' 161', ' 479', ' 201', '2'], ['9068', '186', '429', ' 163', ' 481', ' 204', '2'], ['9069', '186', '431', ' 164', ' 483', ' 205', '2'], ['9070', '186', '431', ' 165', ' 484', ' 207', '2'], ['9071', '186', '431', ' 165', ' 486', ' 209', '2'], ['9072', '186', '432', ' 166', ' 488', ' 210', '2'], ['9073', '186', '431', ' 166', ' 488', ' 212', '2'], ['9074', '186', '433', ' 167', ' 490', ' 213', '2'], ['9075', '186', '433', ' 168', ' 491', ' 215', '2'], ['9076', '186', '434', ' 169', ' 493', ' 217', '2'], ['9077', '186', '435', ' 170', ' 493', ' 218', '2'], ['9078', '186', '435', ' 172', ' 495', ' 221', '2'], ['9079', '186', '437', ' 173', ' 497', ' 223', '2'], ['9080', '186', '439', ' 175', ' 498', ' 225', '2'], ['9081', '186', '440', ' 177', ' 498', ' 226', '2'], ['9082', '186', '442', ' 178', ' 501', ' 227', '2'], ['9083', '186', '443', ' 179', ' 503', ' 229', '2'], ['9084', '186', '442', ' 180', ' 506', ' 233', '2'], ['9085', '186', '443', ' 183', ' 507', ' 236', '2'], ['9086', '186', '445', ' 185', ' 508', ' 238', '2'], ['9087', '186', '445', ' 186', ' 510', ' 240', '2'], ['9088', '186', '447', ' 189', ' 512', ' 242', '2'], ['9089', '186', '449', ' 190', ' 514', ' 245', '2'], ['9090', '186', '451', ' 192', ' 517', ' 247', '2'], ['9091', '186', '452', ' 194', ' 519', ' 250', '2'], ['9092', '186', '452', ' 195', ' 522', ' 253', '2'], ['9093', '186', '453', ' 197', ' 523', ' 256', '2'], ['9094', '186', '454', ' 198', ' 526', ' 258', '2'], ['9095', '186', '455', ' 199', ' 529', ' 261', '2'], ['9096', '186', '457', ' 200', ' 531', ' 262', '2'], ['9097', '186', '458', ' 202', ' 533', ' 266', '2'], ['9098', '186', '458', ' 203', ' 537', ' 271', '2'], ['9099', '186', '459', ' 204', ' 541', ' 274', '2'], ['9100', '186', '462', ' 208', ' 543', ' 277', '2'], ['9101', '186', '464', ' 211', ' 545', ' 280', '2'], ['9102', '186', '465', ' 214', ' 548', ' 285', '2'], ['9103', '186', '468', ' 216', ' 552', ' 288', '2'], ['9104', '186', '469', ' 218', ' 556', ' 293', '2'], ['9105', '186', '470', ' 221', ' 558', ' 297', '2'], ['9106', '186', '473', ' 224', ' 561', ' 300', '2'], ['9107', '186', '474', ' 225', ' 565', ' 304', '2'], ['9108', '186', '476', ' 229', ' 569', ' 310', '2'], ['9109', '186', '479', ' 232', ' 573', ' 313', '2'], ['9110', '186', '481', ' 235', ' 577', ' 319', '2'], ['9111', '186', '484', ' 239', ' 582', ' 324', '2'], ['9112', '186', '487', ' 242', ' 587', ' 329', '2'], ['9113', '186', '489', ' 246', ' 591', ' 335', '2'], ['9114', '186', '490', ' 248', ' 596', ' 340', '2'], ['9115', '186', '493', ' 251', ' 601', ' 346', '2'], ['9116', '186', '496', ' 256', ' 605', ' 351', '2'], ['9117', '186', '499', ' 260', ' 611', ' 358', '2'], ['9118', '186', '502', ' 265', ' 615', ' 365', '2'], ['9119', '186', '505', ' 269', ' 622', ' 372', '2'], ['9120', '186', '508', ' 273', ' 629', ' 380', '2'], ['9121', '186', '511', ' 277', ' 636', ' 388', '2'], ['9122', '186', '513', ' 280', ' 645', ' 398', '2'], ['9123', '186', '517', ' 286', ' 652', ' 407', '2'], ['9124', '186', '522', ' 292', ' 656', ' 413', '2'], ['9125', '186', '530', ' 299', ' 661', ' 416', '2'], ['9126', '186', '537', ' 304', ' 664', ' 416', '2'], ['9127', '186', '546', ' 310', ' 671', ' 417', '2'], ['9128', '186', '554', ' 317', ' 674', ' 417', '2'], ['9129', '186', '560', ' 322', ' 673', ' 414', '2'], ['9130', '186', '565', ' 325', ' 678', ' 414', '2'], ['9131', '186', '576', ' 336', ' 680', ' 415', '2'], ['9132', '186', '590', ' 344', ' 691', ' 415', '2'], ['9133', '186', '599', ' 353', ' 694', ' 414', '2']]}, {'248': [['10400', '248', '364', ' 106', ' 387', ' 120', '2'], ['10401', '248', '364', ' 106', ' 387', ' 120', '2'], ['10402', '248', '364', ' 106', ' 387', ' 120', '2'], ['10403', '248', '364', ' 106', ' 387', ' 120', '2'], ['10404', '248', '363', ' 105', ' 387', ' 120', '2'], ['10405', '248', '364', ' 106', ' 387', ' 120', '2'], ['10406', '248', '364', ' 106', ' 387', ' 121', '2'], ['10407', '248', '364', ' 107', ' 388', ' 121', '2'], ['10413', '248', '364', ' 107', ' 388', ' 121', '2'], ['10414', '248', '364', ' 107', ' 389', ' 122', '2'], ['10415', '248', '364', ' 107', ' 390', ' 122', '2'], ['10416', '248', '364', ' 107', ' 391', ' 123', '2'], ['10417', '248', '364', ' 107', ' 391', ' 124', '2'], ['10418', '248', '364', ' 107', ' 391', ' 125', '2'], ['10419', '248', '364', ' 107', ' 392', ' 125', '2'], ['10420', '248', '363', ' 107', ' 392', ' 125', '2'], ['10421', '248', '363', ' 107', ' 392', ' 126', '2'], ['10422', '248', '364', ' 107', ' 392', ' 126', '2'], ['10423', '248', '365', ' 108', ' 392', ' 126', '2'], ['10424', '248', '365', ' 108', ' 392', ' 127', '2'], ['10425', '248', '364', ' 109', ' 391', ' 127', '2'], ['10426', '248', '364', ' 109', ' 391', ' 127', '2'], ['10427', '248', '364', ' 109', ' 391', ' 127', '2'], ['10428', '248', '364', ' 109', ' 392', ' 127', '2'], ['10429', '248', '363', ' 109', ' 391', ' 128', '2'], ['10430', '248', '363', ' 109', ' 391', ' 128', '2'], ['10431', '248', '363', ' 109', ' 392', ' 129', '2'], ['10432', '248', '364', ' 110', ' 392', ' 129', '2'], ['10433', '248', '364', ' 111', ' 392', ' 130', '2'], ['10434', '248', '363', ' 111', ' 391', ' 131', '2'], ['10435', '248', '363', ' 111', ' 392', ' 131', '2'], ['10436', '248', '363', ' 111', ' 393', ' 131', '2'], ['10437', '248', '364', ' 111', ' 393', ' 132', '2'], ['10438', '248', '364', ' 114', ' 392', ' 132', '2'], ['10439', '248', '366', ' 116', ' 390', ' 133', '2'], ['10440', '248', '366', ' 116', ' 391', ' 133', '2'], ['10441', '248', '365', ' 116', ' 391', ' 134', '2'], ['10442', '248', '365', ' 116', ' 391', ' 134', '2'], ['10443', '248', '364', ' 115', ' 392', ' 134', '2'], ['10444', '248', '365', ' 117', ' 391', ' 134', '2'], ['10445', '248', '365', ' 117', ' 392', ' 135', '2'], ['10446', '248', '366', ' 117', ' 392', ' 135', '2'], ['10447', '248', '365', ' 117', ' 393', ' 135', '2'], ['10448', '248', '364', ' 117', ' 394', ' 136', '2'], ['10449', '248', '364', ' 116', ' 394', ' 137', '2'], ['10450', '248', '364', ' 117', ' 394', ' 137', '2'], ['10451', '248', '365', ' 118', ' 395', ' 139', '2'], ['10452', '248', '366', ' 120', ' 395', ' 139', '2'], ['10453', '248', '366', ' 120', ' 394', ' 140', '2'], ['10454', '248', '365', ' 119', ' 395', ' 140', '2'], ['10455', '248', '364', ' 118', ' 396', ' 141', '2'], ['10456', '248', '363', ' 117', ' 398', ' 142', '2'], ['10457', '248', '361', ' 113', ' 400', ' 143', '2'], ['10458', '248', '361', ' 114', ' 400', ' 143', '2'], ['10459', '248', '361', ' 116', ' 399', ' 144', '2'], ['10460', '248', '361', ' 116', ' 399', ' 145', '2'], ['10461', '248', '361', ' 116', ' 399', ' 145', '2'], ['10462', '248', '362', ' 116', ' 399', ' 146', '2'], ['10463', '248', '362', ' 115', ' 400', ' 146', '2'], ['10464', '248', '363', ' 117', ' 399', ' 147', '2'], ['10465', '248', '364', ' 119', ' 398', ' 147', '2'], ['10466', '248', '366', ' 121', ' 398', ' 148', '2'], ['10467', '248', '365', ' 121', ' 399', ' 150', '2'], ['10468', '248', '365', ' 121', ' 399', ' 150', '2'], ['10469', '248', '365', ' 122', ' 399', ' 151', '2'], ['10470', '248', '366', ' 125', ' 398', ' 152', '2'], ['10471', '248', '366', ' 125', ' 397', ' 152', '2'], ['10472', '248', '366', ' 126', ' 397', ' 152', '2'], ['10473', '248', '366', ' 127', ' 398', ' 153', '2'], ['10474', '248', '366', ' 127', ' 399', ' 154', '2'], ['10475', '248', '366', ' 127', ' 399', ' 155', '2'], ['10476', '248', '366', ' 126', ' 400', ' 155', '2'], ['10477', '248', '365', ' 127', ' 401', ' 157', '2'], ['10478', '248', '366', ' 129', ' 400', ' 158', '2'], ['10479', '248', '365', ' 128', ' 401', ' 158', '2'], ['10480', '248', '365', ' 129', ' 402', ' 160', '2'], ['10481', '248', '366', ' 129', ' 403', ' 162', '2'], ['10482', '248', '365', ' 131', ' 403', ' 164', '2'], ['10483', '248', '365', ' 131', ' 403', ' 165', '2'], ['10484', '248', '366', ' 132', ' 404', ' 166', '2'], ['10485', '248', '366', ' 133', ' 405', ' 167', '2'], ['10486', '248', '366', ' 133', ' 406', ' 169', '2'], ['10487', '248', '367', ' 134', ' 406', ' 170', '2'], ['10488', '248', '366', ' 135', ' 406', ' 171', '2'], ['10489', '248', '366', ' 136', ' 406', ' 172', '2'], ['10490', '248', '366', ' 136', ' 407', ' 173', '2'], ['10491', '248', '366', ' 136', ' 408', ' 175', '2'], ['10492', '248', '366', ' 136', ' 409', ' 176', '2'], ['10493', '248', '367', ' 138', ' 410', ' 177', '2'], ['10494', '248', '367', ' 138', ' 411', ' 179', '2'], ['10495', '248', '368', ' 140', ' 410', ' 180', '2'], ['10496', '248', '367', ' 140', ' 410', ' 182', '2'], ['10497', '248', '367', ' 142', ' 411', ' 184', '2'], ['10498', '248', '368', ' 142', ' 411', ' 183', '2'], ['10499', '248', '368', ' 143', ' 411', ' 185', '2'], ['10500', '248', '369', ' 144', ' 413', ' 187', '2'], ['10501', '248', '369', ' 147', ' 414', ' 190', '2'], ['10502', '248', '370', ' 148', ' 415', ' 191', '2'], ['10503', '248', '370', ' 149', ' 416', ' 193', '2'], ['10504', '248', '370', ' 149', ' 417', ' 195', '2'], ['10505', '248', '370', ' 150', ' 418', ' 196', '2'], ['10506', '248', '370', ' 151', ' 419', ' 199', '2'], ['10507', '248', '371', ' 154', ' 420', ' 202', '2'], ['10508', '248', '372', ' 156', ' 420', ' 204', '2'], ['10509', '248', '372', ' 158', ' 421', ' 206', '2'], ['10510', '248', '373', ' 159', ' 423', ' 208', '2'], ['10511', '248', '373', ' 160', ' 424', ' 210', '2'], ['10512', '248', '373', ' 162', ' 425', ' 212', '2'], ['10513', '248', '373', ' 162', ' 427', ' 215', '2'], ['10514', '248', '372', ' 162', ' 429', ' 218', '2'], ['10515', '248', '373', ' 163', ' 430', ' 220', '2'], ['10516', '248', '373', ' 167', ' 431', ' 224', '2'], ['10517', '248', '373', ' 167', ' 432', ' 226', '2'], ['10518', '248', '374', ' 169', ' 433', ' 228', '2'], ['10519', '248', '376', ' 173', ' 435', ' 232', '2'], ['10520', '248', '376', ' 172', ' 438', ' 235', '2'], ['10521', '248', '376', ' 173', ' 440', ' 238', '2'], ['10522', '248', '376', ' 174', ' 442', ' 242', '2'], ['10523', '248', '376', ' 177', ' 444', ' 247', '2'], ['10524', '248', '376', ' 179', ' 445', ' 250', '2'], ['10525', '248', '377', ' 182', ' 447', ' 253', '2'], ['10526', '248', '378', ' 183', ' 448', ' 256', '2'], ['10527', '248', '379', ' 187', ' 452', ' 262', '2'], ['10528', '248', '379', ' 188', ' 454', ' 267', '2'], ['10529', '248', '380', ' 191', ' 456', ' 271', '2'], ['10530', '248', '381', ' 193', ' 458', ' 274', '2'], ['10531', '248', '381', ' 196', ' 461', ' 281', '2'], ['10532', '248', '382', ' 199', ' 463', ' 286', '2'], ['10533', '248', '383', ' 203', ' 466', ' 293', '2'], ['10534', '248', '384', ' 205', ' 469', ' 297', '2'], ['10535', '248', '386', ' 209', ' 472', ' 302', '2'], ['10536', '248', '387', ' 213', ' 476', ' 308', '2'], ['10537', '248', '388', ' 217', ' 480', ' 316', '2'], ['10538', '248', '390', ' 221', ' 485', ' 323', '2'], ['10539', '248', '390', ' 224', ' 489', ' 330', '2'], ['10540', '248', '391', ' 229', ' 493', ' 337', '2'], ['10541', '248', '393', ' 232', ' 499', ' 345', '2'], ['10542', '248', '395', ' 238', ' 503', ' 353', '2'], ['10543', '248', '396', ' 242', ' 509', ' 362', '2'], ['10544', '248', '396', ' 247', ' 514', ' 373', '2'], ['10545', '248', '398', ' 250', ' 522', ' 383', '2'], ['10546', '248', '397', ' 256', ' 530', ' 399', '2'], ['10547', '248', '400', ' 263', ' 538', ' 410', '2'], ['10548', '248', '405', ' 269', ' 542', ' 415', '2'], ['10549', '248', '410', ' 275', ' 544', ' 417', '2'], ['10550', '248', '416', ' 281', ' 548', ' 418', '2'], ['10551', '248', '427', ' 290', ' 540', ' 402', '2'], ['10552', '248', '435', ' 298', ' 546', ' 405', '2'], ['10553', '248', '437', ' 306', ' 552', ' 413', '2'], ['10554', '248', '445', ' 316', ' 558', ' 416', '2'], ['10555', '248', '450', ' 325', ' 557', ' 415', '2']]}, {'261': [['10641', '261', '370', ' 106', ' 390', ' 119', '2'], ['10642', '261', '370', ' 105', ' 390', ' 118', '2'], ['10643', '261', '370', ' 106', ' 390', ' 119', '2'], ['10644', '261', '370', ' 107', ' 391', ' 120', '2'], ['10645', '261', '370', ' 107', ' 392', ' 121', '2'], ['10646', '261', '370', ' 108', ' 392', ' 122', '2'], ['10647', '261', '371', ' 108', ' 392', ' 122', '2'], ['10648', '261', '371', ' 109', ' 392', ' 122', '2'], ['10649', '261', '371', ' 108', ' 393', ' 122', '2'], ['10650', '261', '371', ' 108', ' 394', ' 122', '2'], ['10651', '261', '371', ' 108', ' 395', ' 123', '2'], ['10652', '261', '371', ' 109', ' 396', ' 124', '2'], ['10653', '261', '372', ' 109', ' 397', ' 125', '2'], ['10654', '261', '372', ' 109', ' 397', ' 126', '2'], ['10655', '261', '372', ' 110', ' 397', ' 126', '2'], ['10656', '261', '371', ' 108', ' 399', ' 126', '2'], ['10657', '261', '372', ' 108', ' 400', ' 127', '2'], ['10658', '261', '372', ' 108', ' 400', ' 127', '2'], ['10659', '261', '372', ' 108', ' 401', ' 127', '2'], ['10660', '261', '373', ' 108', ' 401', ' 127', '2'], ['10661', '261', '372', ' 108', ' 401', ' 128', '2'], ['10662', '261', '373', ' 108', ' 402', ' 129', '2'], ['10663', '261', '374', ' 110', ' 402', ' 130', '2'], ['10664', '261', '374', ' 110', ' 403', ' 130', '2'], ['10665', '261', '375', ' 112', ' 403', ' 131', '2'], ['10666', '261', '375', ' 113', ' 403', ' 132', '2'], ['10667', '261', '376', ' 115', ' 403', ' 132', '2'], ['10668', '261', '379', ' 117', ' 403', ' 133', '2'], ['10669', '261', '379', ' 118', ' 404', ' 134', '2'], ['10670', '261', '378', ' 117', ' 405', ' 135', '2'], ['10671', '261', '378', ' 117', ' 406', ' 135', '2'], ['10672', '261', '378', ' 118', ' 406', ' 136', '2'], ['10673', '261', '378', ' 117', ' 408', ' 137', '2'], ['10674', '261', '378', ' 118', ' 409', ' 138', '2'], ['10675', '261', '379', ' 118', ' 409', ' 139', '2'], ['10676', '261', '379', ' 119', ' 410', ' 139', '2'], ['10677', '261', '379', ' 119', ' 411', ' 140', '2'], ['10678', '261', '379', ' 119', ' 412', ' 140', '2'], ['10679', '261', '380', ' 118', ' 413', ' 140', '2'], ['10680', '261', '380', ' 118', ' 413', ' 141', '2'], ['10681', '261', '380', ' 119', ' 413', ' 142', '2'], ['10682', '261', '380', ' 120', ' 413', ' 143', '2'], ['10683', '261', '380', ' 121', ' 414', ' 144', '2'], ['10684', '261', '381', ' 121', ' 414', ' 145', '2'], ['10685', '261', '381', ' 122', ' 415', ' 146', '2'], ['10686', '261', '383', ' 124', ' 415', ' 147', '2'], ['10687', '261', '383', ' 124', ' 417', ' 147', '2'], ['10688', '261', '384', ' 125', ' 419', ' 150', '2'], ['10689', '261', '384', ' 125', ' 420', ' 151', '2'], ['10690', '261', '385', ' 126', ' 421', ' 152', '2'], ['10691', '261', '385', ' 127', ' 421', ' 153', '2'], ['10692', '261', '385', ' 128', ' 422', ' 154', '2'], ['10693', '261', '386', ' 128', ' 423', ' 155', '2'], ['10694', '261', '387', ' 129', ' 424', ' 156', '2'], ['10695', '261', '387', ' 130', ' 424', ' 156', '2'], ['10696', '261', '387', ' 130', ' 425', ' 158', '2'], ['10697', '261', '388', ' 130', ' 427', ' 159', '2'], ['10698', '261', '388', ' 130', ' 428', ' 160', '2'], ['10699', '261', '389', ' 132', ' 428', ' 161', '2'], ['10700', '261', '390', ' 133', ' 430', ' 162', '2'], ['10701', '261', '392', ' 134', ' 433', ' 165', '2'], ['10702', '261', '392', ' 134', ' 435', ' 166', '2'], ['10703', '261', '392', ' 135', ' 435', ' 168', '2'], ['10704', '261', '392', ' 135', ' 437', ' 169', '2'], ['10705', '261', '393', ' 136', ' 438', ' 171', '2'], ['10706', '261', '394', ' 137', ' 440', ' 172', '2'], ['10707', '261', '395', ' 138', ' 441', ' 174', '2'], ['10708', '261', '396', ' 140', ' 441', ' 175', '2'], ['10709', '261', '398', ' 141', ' 441', ' 175', '2'], ['10710', '261', '398', ' 142', ' 443', ' 177', '2'], ['10711', '261', '400', ' 143', ' 445', ' 178', '2'], ['10712', '261', '401', ' 145', ' 446', ' 180', '2'], ['10713', '261', '401', ' 146', ' 448', ' 182', '2'], ['10714', '261', '402', ' 147', ' 449', ' 184', '2'], ['10715', '261', '402', ' 146', ' 452', ' 186', '2'], ['10716', '261', '403', ' 147', ' 454', ' 188', '2'], ['10717', '261', '404', ' 148', ' 456', ' 190', '2'], ['10718', '261', '406', ' 150', ' 457', ' 191', '2'], ['10719', '261', '409', ' 152', ' 460', ' 194', '2'], ['10720', '261', '409', ' 153', ' 462', ' 197', '2'], ['10721', '261', '411', ' 155', ' 464', ' 199', '2'], ['10722', '261', '412', ' 157', ' 466', ' 201', '2'], ['10723', '261', '413', ' 158', ' 467', ' 203', '2'], ['10724', '261', '414', ' 160', ' 469', ' 206', '2'], ['10725', '261', '415', ' 161', ' 470', ' 207', '2'], ['10726', '261', '416', ' 162', ' 473', ' 210', '2'], ['10727', '261', '417', ' 163', ' 475', ' 212', '2'], ['10728', '261', '419', ' 165', ' 477', ' 214', '2'], ['10729', '261', '420', ' 166', ' 480', ' 217', '2'], ['10730', '261', '422', ' 168', ' 483', ' 221', '2'], ['10731', '261', '423', ' 172', ' 485', ' 225', '2'], ['10732', '261', '425', ' 173', ' 487', ' 227', '2'], ['10733', '261', '428', ' 176', ' 491', ' 229', '2'], ['10734', '261', '429', ' 178', ' 494', ' 233', '2'], ['10735', '261', '430', ' 179', ' 497', ' 236', '2'], ['10736', '261', '432', ' 181', ' 500', ' 239', '2'], ['10737', '261', '434', ' 183', ' 504', ' 244', '2'], ['10738', '261', '436', ' 185', ' 507', ' 246', '2'], ['10739', '261', '438', ' 189', ' 510', ' 250', '2'], ['10740', '261', '439', ' 191', ' 514', ' 255', '2'], ['10741', '261', '440', ' 192', ' 520', ' 260', '2'], ['10742', '261', '442', ' 194', ' 523', ' 264', '2'], ['10743', '261', '443', ' 196', ' 528', ' 270', '2'], ['10744', '261', '447', ' 201', ' 531', ' 274', '2'], ['10745', '261', '450', ' 203', ' 535', ' 278', '2'], ['10746', '261', '452', ' 205', ' 541', ' 284', '2'], ['10747', '261', '455', ' 209', ' 546', ' 289', '2'], ['10748', '261', '458', ' 213', ' 551', ' 296', '2'], ['10749', '261', '462', ' 217', ' 556', ' 301', '2'], ['10750', '261', '464', ' 220', ' 562', ' 307', '2'], ['10751', '261', '468', ' 224', ' 568', ' 313', '2'], ['10752', '261', '471', ' 228', ' 575', ' 320', '2'], ['10753', '261', '474', ' 232', ' 581', ' 327', '2'], ['10754', '261', '478', ' 236', ' 588', ' 334', '2'], ['10755', '261', '482', ' 242', ' 594', ' 342', '2'], ['10756', '261', '486', ' 246', ' 602', ' 350', '2'], ['10757', '261', '490', ' 250', ' 611', ' 359', '2'], ['10758', '261', '494', ' 256', ' 619', ' 369', '2'], ['10759', '261', '500', ' 262', ' 628', ' 377', '2'], ['10760', '261', '505', ' 268', ' 638', ' 388', '2'], ['10761', '261', '509', ' 273', ' 650', ' 401', '2'], ['10762', '261', '514', ' 279', ' 659', ' 411', '2'], ['10763', '261', '523', ' 286', ' 665', ' 415', '2'], ['10764', '261', '535', ' 293', ' 674', ' 417', '2'], ['10765', '261', '545', ' 301', ' 680', ' 418', '2'], ['10766', '261', '564', ' 310', ' 696', ' 417', '2'], ['10767', '261', '568', ' 319', ' 691', ' 416', '2'], ['10768', '261', '578', ' 324', ' 700', ' 416', '2'], ['10769', '261', '590', ' 336', ' 704', ' 416', '2'], ['10770', '261', '600', ' 346', ' 704', ' 415', '2']]}, {'274': [['11230', '274', '374', ' 104', ' 396', ' 120', '2'], ['11231', '274', '374', ' 104', ' 396', ' 120', '2'], ['11232', '274', '375', ' 105', ' 396', ' 121', '2'], ['11233', '274', '376', ' 106', ' 396', ' 121', '2'], ['11237', '274', '376', ' 107', ' 396', ' 122', '2'], ['11238', '274', '376', ' 107', ' 397', ' 122', '2'], ['11242', '274', '376', ' 107', ' 398', ' 123', '2'], ['11243', '274', '376', ' 107', ' 399', ' 124', '2'], ['11244', '274', '376', ' 108', ' 400', ' 125', '2'], ['11245', '274', '377', ' 108', ' 401', ' 126', '2'], ['11246', '274', '378', ' 108', ' 401', ' 126', '2'], ['11247', '274', '378', ' 108', ' 402', ' 126', '2'], ['11248', '274', '379', ' 108', ' 402', ' 126', '2'], ['11249', '274', '380', ' 109', ' 403', ' 127', '2'], ['11250', '274', '379', ' 107', ' 406', ' 127', '2'], ['11251', '274', '380', ' 107', ' 406', ' 128', '2'], ['11252', '274', '381', ' 107', ' 406', ' 128', '2'], ['11253', '274', '381', ' 108', ' 407', ' 128', '2'], ['11254', '274', '381', ' 108', ' 407', ' 129', '2'], ['11255', '274', '382', ' 108', ' 408', ' 129', '2'], ['11256', '274', '383', ' 108', ' 408', ' 129', '2'], ['11257', '274', '383', ' 108', ' 408', ' 129', '2'], ['11258', '274', '383', ' 109', ' 408', ' 129', '2'], ['11259', '274', '383', ' 108', ' 409', ' 129', '2'], ['11260', '274', '384', ' 108', ' 409', ' 130', '2'], ['11261', '274', '384', ' 109', ' 410', ' 130', '2'], ['11262', '274', '385', ' 111', ' 409', ' 131', '2'], ['11263', '274', '385', ' 112', ' 409', ' 131', '2'], ['11264', '274', '386', ' 112', ' 410', ' 132', '2'], ['11265', '274', '386', ' 112', ' 411', ' 132', '2'], ['11266', '274', '388', ' 114', ' 411', ' 133', '2'], ['11267', '274', '388', ' 115', ' 412', ' 133', '2'], ['11268', '274', '388', ' 113', ' 413', ' 134', '2'], ['11269', '274', '389', ' 114', ' 414', ' 134', '2'], ['11270', '274', '389', ' 114', ' 414', ' 134', '2'], ['11271', '274', '390', ' 114', ' 414', ' 134', '2'], ['11272', '274', '390', ' 114', ' 416', ' 134', '2'], ['11273', '274', '390', ' 114', ' 416', ' 134', '2'], ['11274', '274', '391', ' 114', ' 417', ' 135', '2'], ['11275', '274', '391', ' 114', ' 418', ' 136', '2'], ['11276', '274', '392', ' 115', ' 419', ' 137', '2'], ['11277', '274', '391', ' 115', ' 420', ' 138', '2'], ['11278', '274', '392', ' 116', ' 420', ' 138', '2'], ['11279', '274', '394', ' 118', ' 421', ' 139', '2'], ['11280', '274', '394', ' 118', ' 421', ' 140', '2'], ['11281', '274', '393', ' 117', ' 422', ' 140', '2'], ['11282', '274', '394', ' 117', ' 422', ' 140', '2'], ['11283', '274', '395', ' 117', ' 422', ' 140', '2'], ['11284', '274', '396', ' 117', ' 422', ' 139', '2'], ['11285', '274', '396', ' 118', ' 424', ' 141', '2'], ['11286', '274', '395', ' 118', ' 425', ' 142', '2'], ['11287', '274', '396', ' 118', ' 425', ' 142', '2'], ['11288', '274', '396', ' 117', ' 426', ' 143', '2'], ['11289', '274', '396', ' 117', ' 427', ' 143', '2'], ['11290', '274', '396', ' 117', ' 428', ' 145', '2'], ['11291', '274', '397', ' 117', ' 429', ' 146', '2'], ['11292', '274', '397', ' 118', ' 429', ' 146', '2'], ['11293', '274', '398', ' 118', ' 430', ' 147', '2'], ['11294', '274', '399', ' 119', ' 430', ' 147', '2'], ['11295', '274', '400', ' 120', ' 430', ' 147', '2'], ['11296', '274', '400', ' 120', ' 431', ' 148', '2'], ['11297', '274', '401', ' 120', ' 433', ' 149', '2'], ['11298', '274', '402', ' 120', ' 434', ' 150', '2'], ['11299', '274', '402', ' 121', ' 434', ' 150', '2'], ['11300', '274', '402', ' 121', ' 435', ' 151', '2'], ['11301', '274', '403', ' 122', ' 436', ' 152', '2'], ['11302', '274', '403', ' 122', ' 436', ' 153', '2'], ['11303', '274', '404', ' 123', ' 437', ' 154', '2'], ['11304', '274', '405', ' 124', ' 438', ' 154', '2'], ['11305', '274', '406', ' 124', ' 439', ' 155', '2'], ['11306', '274', '406', ' 125', ' 439', ' 155', '2'], ['11307', '274', '407', ' 125', ' 440', ' 156', '2'], ['11308', '274', '408', ' 126', ' 442', ' 158', '2'], ['11309', '274', '408', ' 127', ' 443', ' 159', '2'], ['11310', '274', '408', ' 127', ' 444', ' 160', '2'], ['11311', '274', '410', ' 128', ' 445', ' 160', '2'], ['11312', '274', '411', ' 129', ' 446', ' 161', '2'], ['11313', '274', '411', ' 129', ' 447', ' 162', '2'], ['11314', '274', '413', ' 130', ' 448', ' 163', '2'], ['11315', '274', '413', ' 131', ' 449', ' 164', '2'], ['11316', '274', '413', ' 131', ' 451', ' 165', '2'], ['11317', '274', '414', ' 132', ' 452', ' 166', '2'], ['11318', '274', '415', ' 132', ' 453', ' 166', '2'], ['11319', '274', '415', ' 131', ' 455', ' 168', '2'], ['11320', '274', '416', ' 133', ' 455', ' 169', '2'], ['11321', '274', '417', ' 133', ' 457', ' 171', '2'], ['11322', '274', '417', ' 133', ' 457', ' 172', '2'], ['11323', '274', '418', ' 133', ' 458', ' 173', '2'], ['11324', '274', '419', ' 134', ' 460', ' 173', '2'], ['11325', '274', '421', ' 135', ' 461', ' 174', '2'], ['11326', '274', '421', ' 136', ' 462', ' 176', '2'], ['11327', '274', '423', ' 136', ' 464', ' 177', '2'], ['11328', '274', '424', ' 138', ' 463', ' 177', '2'], ['11329', '274', '425', ' 139', ' 464', ' 178', '2'], ['11330', '274', '425', ' 139', ' 465', ' 179', '2'], ['11331', '274', '425', ' 140', ' 466', ' 181', '2'], ['11332', '274', '426', ' 141', ' 467', ' 182', '2'], ['11333', '274', '426', ' 142', ' 468', ' 184', '2'], ['11334', '274', '427', ' 143', ' 469', ' 185', '2'], ['11335', '274', '428', ' 143', ' 471', ' 186', '2'], ['11336', '274', '429', ' 144', ' 473', ' 187', '2'], ['11337', '274', '430', ' 145', ' 474', ' 189', '2'], ['11338', '274', '431', ' 146', ' 475', ' 190', '2'], ['11339', '274', '432', ' 147', ' 476', ' 191', '2'], ['11340', '274', '432', ' 148', ' 478', ' 193', '2'], ['11341', '274', '434', ' 150', ' 479', ' 195', '2'], ['11342', '274', '433', ' 150', ' 481', ' 197', '2'], ['11343', '274', '435', ' 151', ' 482', ' 198', '2'], ['11344', '274', '437', ' 152', ' 485', ' 200', '2'], ['11345', '274', '438', ' 153', ' 487', ' 202', '2'], ['11346', '274', '439', ' 155', ' 489', ' 204', '2'], ['11347', '274', '441', ' 156', ' 490', ' 206', '2'], ['11348', '274', '442', ' 157', ' 492', ' 207', '2'], ['11349', '274', '443', ' 158', ' 493', ' 208', '2'], ['11350', '274', '443', ' 159', ' 495', ' 209', '2'], ['11351', '274', '443', ' 159', ' 497', ' 211', '2'], ['11352', '274', '445', ' 160', ' 498', ' 213', '2'], ['11353', '274', '446', ' 161', ' 501', ' 216', '2'], ['11354', '274', '447', ' 163', ' 503', ' 219', '2'], ['11355', '274', '448', ' 164', ' 505', ' 220', '2'], ['11356', '274', '450', ' 166', ' 508', ' 223', '2'], ['11357', '274', '450', ' 167', ' 510', ' 226', '2'], ['11358', '274', '451', ' 167', ' 512', ' 228', '2'], ['11359', '274', '458', ' 172', ' 516', ' 230', '2'], ['11360', '274', '457', ' 171', ' 518', ' 232', '2'], ['11361', '274', '459', ' 174', ' 522', ' 236', '2'], ['11362', '274', '463', ' 177', ' 525', ' 239', '2'], ['11363', '274', '461', ' 176', ' 525', ' 241', '2'], ['11364', '274', '462', ' 177', ' 529', ' 245', '2'], ['11365', '274', '463', ' 178', ' 533', ' 249', '2'], ['11367', '274', '466', ' 182', ' 536', ' 252', '2'], ['11368', '274', '473', ' 190', ' 540', ' 257', '2'], ['11369', '274', '474', ' 191', ' 544', ' 260', '2'], ['11370', '274', '473', ' 188', ' 548', ' 264', '2'], ['11371', '274', '474', ' 190', ' 552', ' 267', '2'], ['11372', '274', '481', ' 196', ' 556', ' 272', '2'], ['11373', '274', '484', ' 203', ' 558', ' 277', '2'], ['11374', '274', '485', ' 204', ' 561', ' 279', '2'], ['11375', '274', '484', ' 201', ' 567', ' 283', '2'], ['11376', '274', '485', ' 201', ' 572', ' 288', '2'], ['11377', '274', '486', ' 202', ' 577', ' 293', '2'], ['11378', '274', '488', ' 204', ' 582', ' 297', '2'], ['11379', '274', '491', ' 206', ' 587', ' 302', '2'], ['11380', '274', '494', ' 209', ' 591', ' 306', '2'], ['11381', '274', '497', ' 213', ' 596', ' 312', '2'], ['11382', '274', '500', ' 217', ' 601', ' 318', '2'], ['11383', '274', '503', ' 219', ' 607', ' 324', '2'], ['11384', '274', '507', ' 222', ' 613', ' 329', '2'], ['11385', '274', '510', ' 224', ' 619', ' 333', '2'], ['11386', '274', '514', ' 228', ' 626', ' 341', '2'], ['11387', '274', '516', ' 231', ' 633', ' 349', '2'], ['11388', '274', '520', ' 235', ' 639', ' 355', '2'], ['11389', '274', '526', ' 240', ' 647', ' 363', '2'], ['11390', '274', '528', ' 243', ' 654', ' 370', '2'], ['11391', '274', '532', ' 247', ' 663', ' 380', '2'], ['11392', '274', '537', ' 252', ' 672', ' 389', '2'], ['11393', '274', '540', ' 256', ' 682', ' 401', '2'], ['11394', '274', '546', ' 262', ' 691', ' 410', '2'], ['11395', '274', '554', ' 267', ' 699', ' 413', '2'], ['11396', '274', '566', ' 273', ' 711', ' 417', '2'], ['11397', '274', '577', ' 277', ' 723', ' 419', '2'], ['11398', '274', '582', ' 280', ' 731', ' 422', '2'], ['11399', '274', '590', ' 288', ' 732', ' 420', '2'], ['11400', '274', '597', ' 296', ' 734', ' 418', '2'], ['11401', '274', '606', ' 303', ' 738', ' 417', '2'], ['11402', '274', '616', ' 310', ' 744', ' 416', '2'], ['11403', '274', '625', ' 318', ' 749', ' 416', '2'], ['11404', '274', '636', ' 326', ' 753', ' 415', '2'], ['11405', '274', '642', ' 331', ' 759', ' 416', '2']]}, {'367': [['13909', '367', '365', ' 109', ' 393', ' 137', '2'], ['13922', '367', '370', ' 113', ' 401', ' 145', '2'], ['13923', '367', '370', ' 114', ' 401', ' 146', '2'], ['13924', '367', '371', ' 115', ' 401', ' 147', '2'], ['13931', '367', '375', ' 124', ' 403', ' 152', '2'], ['13932', '367', '376', ' 125', ' 404', ' 153', '2'], ['13933', '367', '376', ' 125', ' 405', ' 153', '2'], ['13934', '367', '377', ' 127', ' 405', ' 154', '2'], ['13935', '367', '376', ' 126', ' 407', ' 155', '2'], ['13938', '367', '377', ' 128', ' 409', ' 158', '2'], ['13939', '367', '377', ' 129', ' 409', ' 159', '2'], ['13940', '367', '377', ' 129', ' 410', ' 160', '2'], ['13942', '367', '376', ' 128', ' 414', ' 164', '2'], ['13943', '367', '377', ' 128', ' 415', ' 165', '2'], ['13944', '367', '378', ' 129', ' 416', ' 166', '2'], ['13945', '367', '378', ' 130', ' 416', ' 167', '2'], ['13946', '367', '379', ' 131', ' 417', ' 168', '2'], ['13947', '367', '380', ' 131', ' 418', ' 169', '2'], ['13950', '367', '381', ' 134', ' 420', ' 173', '2'], ['13956', '367', '385', ' 138', ' 427', ' 181', '2'], ['13959', '367', '387', ' 141', ' 429', ' 185', '2'], ['13961', '367', '389', ' 146', ' 430', ' 187', '2'], ['13962', '367', '390', ' 146', ' 431', ' 188', '2'], ['13963', '367', '392', ' 147', ' 433', ' 189', '2'], ['13964', '367', '393', ' 148', ' 435', ' 191', '2'], ['13965', '367', '393', ' 149', ' 436', ' 194', '2'], ['13966', '367', '393', ' 150', ' 437', ' 196', '2'], ['13967', '367', '393', ' 150', ' 439', ' 198', '2'], ['13968', '367', '394', ' 152', ' 441', ' 201', '2'], ['13969', '367', '395', ' 152', ' 442', ' 202', '2'], ['13970', '367', '396', ' 153', ' 443', ' 204', '2'], ['13971', '367', '397', ' 157', ' 444', ' 206', '2'], ['13972', '367', '397', ' 154', ' 448', ' 208', '2'], ['13973', '367', '399', ' 157', ' 449', ' 210', '2'], ['13974', '367', '399', ' 158', ' 451', ' 213', '2'], ['13975', '367', '401', ' 161', ' 452', ' 216', '2'], ['13976', '367', '401', ' 161', ' 454', ' 218', '2'], ['13977', '367', '402', ' 163', ' 456', ' 220', '2'], ['13978', '367', '403', ' 165', ' 458', ' 223', '2'], ['13979', '367', '403', ' 166', ' 460', ' 226', '2'], ['13980', '367', '403', ' 166', ' 462', ' 228', '2'], ['13981', '367', '407', ' 169', ' 465', ' 230', '2'], ['13982', '367', '408', ' 169', ' 469', ' 233', '2'], ['13983', '367', '408', ' 170', ' 471', ' 236', '2'], ['13984', '367', '409', ' 172', ' 473', ' 239', '2'], ['13985', '367', '410', ' 173', ' 476', ' 243', '2'], ['13986', '367', '411', ' 174', ' 480', ' 247', '2'], ['13987', '367', '412', ' 177', ' 483', ' 251', '2'], ['13988', '367', '414', ' 179', ' 486', ' 254', '2'], ['13989', '367', '417', ' 182', ' 489', ' 259', '2'], ['13990', '367', '418', ' 184', ' 492', ' 262', '2'], ['13991', '367', '419', ' 185', ' 495', ' 265', '2'], ['13992', '367', '421', ' 189', ' 499', ' 270', '2'], ['13993', '367', '422', ' 190', ' 502', ' 274', '2'], ['13994', '367', '424', ' 193', ' 506', ' 278', '2'], ['13995', '367', '425', ' 195', ' 511', ' 284', '2'], ['13996', '367', '428', ' 197', ' 515', ' 289', '2'], ['13997', '367', '430', ' 200', ' 519', ' 294', '2'], ['13998', '367', '432', ' 202', ' 524', ' 300', '2'], ['13999', '367', '434', ' 206', ' 528', ' 304', '2'], ['14000', '367', '437', ' 210', ' 532', ' 311', '2'], ['14001', '367', '440', ' 214', ' 537', ' 316', '2'], ['14002', '367', '442', ' 217', ' 543', ' 323', '2'], ['14003', '367', '445', ' 220', ' 550', ' 330', '2'], ['14004', '367', '448', ' 223', ' 556', ' 337', '2'], ['14005', '367', '451', ' 227', ' 562', ' 345', '2'], ['14006', '367', '453', ' 232', ' 567', ' 351', '2'], ['14007', '367', '457', ' 237', ' 574', ' 360', '2'], ['14008', '367', '460', ' 241', ' 582', ' 370', '2'], ['14009', '367', '464', ' 245', ' 590', ' 377', '2'], ['14010', '367', '468', ' 250', ' 598', ' 387', '2'], ['14012', '367', '476', ' 261', ' 616', ' 409', '2'], ['14013', '367', '483', ' 267', ' 623', ' 415', '2'], ['14014', '367', '491', ' 272', ' 630', ' 417', '2'], ['14015', '367', '502', ' 278', ' 640', ' 418', '2'], ['14016', '367', '507', ' 285', ' 637', ' 416', '2'], ['14017', '367', '517', ' 293', ' 641', ' 414', '2'], ['14018', '367', '525', ' 301', ' 647', ' 415', '2'], ['14019', '367', '534', ' 309', ' 652', ' 416', '2'], ['14020', '367', '542', ' 317', ' 656', ' 415', '2'], ['14021', '367', '553', ' 325', ' 664', ' 415', '2'], ['14022', '367', '566', ' 336', ' 669', ' 415', '2']]}, {'369': [['13953', '369', '380', ' 107', ' 409', ' 129', '2'], ['13954', '369', '380', ' 107', ' 409', ' 130', '2'], ['13955', '369', '380', ' 107', ' 409', ' 131', '2'], ['13956', '369', '380', ' 108', ' 409', ' 131', '2'], ['13957', '369', '380', ' 108', ' 409', ' 131', '2'], ['13958', '369', '380', ' 108', ' 409', ' 131', '2'], ['13959', '369', '381', ' 108', ' 409', ' 131', '2'], ['13960', '369', '380', ' 107', ' 410', ' 131', '2'], ['13961', '369', '381', ' 107', ' 410', ' 131', '2'], ['13962', '369', '381', ' 107', ' 410', ' 131', '2'], ['13963', '369', '381', ' 107', ' 410', ' 132', '2'], ['13964', '369', '382', ' 108', ' 411', ' 132', '2'], ['13965', '369', '382', ' 108', ' 411', ' 133', '2'], ['13966', '369', '383', ' 109', ' 412', ' 133', '2'], ['13970', '369', '384', ' 109', ' 413', ' 134', '2'], ['13971', '369', '385', ' 110', ' 413', ' 135', '2'], ['13975', '369', '387', ' 112', ' 415', ' 137', '2'], ['13976', '369', '388', ' 114', ' 414', ' 137', '2'], ['13977', '369', '389', ' 116', ' 414', ' 137', '2'], ['13978', '369', '389', ' 117', ' 414', ' 138', '2'], ['13979', '369', '388', ' 116', ' 414', ' 139', '2'], ['13980', '369', '388', ' 117', ' 414', ' 139', '2'], ['13981', '369', '390', ' 117', ' 415', ' 139', '2'], ['13982', '369', '389', ' 117', ' 416', ' 140', '2'], ['13983', '369', '390', ' 117', ' 417', ' 140', '2'], ['13984', '369', '391', ' 118', ' 418', ' 141', '2'], ['13985', '369', '392', ' 119', ' 418', ' 141', '2'], ['13986', '369', '392', ' 120', ' 418', ' 141', '2'], ['13987', '369', '391', ' 118', ' 419', ' 141', '2'], ['13988', '369', '392', ' 117', ' 419', ' 140', '2'], ['13989', '369', '391', ' 116', ' 421', ' 141', '2'], ['13990', '369', '391', ' 115', ' 422', ' 141', '2'], ['13991', '369', '390', ' 114', ' 422', ' 142', '2'], ['13992', '369', '391', ' 114', ' 423', ' 142', '2'], ['13993', '369', '393', ' 116', ' 422', ' 142', '2'], ['13994', '369', '394', ' 118', ' 422', ' 143', '2'], ['14003', '369', '400', ' 126', ' 424', ' 147', '2'], ['14004', '369', '399', ' 125', ' 426', ' 148', '2'], ['14006', '369', '399', ' 125', ' 427', ' 148', '2'], ['14007', '369', '398', ' 124', ' 430', ' 149', '2'], ['14008', '369', '398', ' 123', ' 432', ' 150', '2'], ['14009', '369', '398', ' 124', ' 433', ' 152', '2'], ['14010', '369', '399', ' 126', ' 433', ' 152', '2'], ['14011', '369', '399', ' 125', ' 434', ' 152', '2'], ['14012', '369', '401', ' 127', ' 433', ' 152', '2'], ['14013', '369', '401', ' 127', ' 435', ' 153', '2'], ['14014', '369', '402', ' 128', ' 435', ' 153', '2'], ['14015', '369', '401', ' 128', ' 435', ' 154', '2'], ['14016', '369', '403', ' 129', ' 435', ' 154', '2'], ['14017', '369', '403', ' 130', ' 435', ' 155', '2'], ['14018', '369', '403', ' 130', ' 437', ' 155', '2'], ['14019', '369', '402', ' 129', ' 437', ' 156', '2'], ['14020', '369', '402', ' 129', ' 438', ' 156', '2'], ['14021', '369', '403', ' 128', ' 439', ' 156', '2'], ['14022', '369', '401', ' 126', ' 441', ' 157', '2'], ['14023', '369', '401', ' 125', ' 441', ' 158', '2'], ['14024', '369', '402', ' 126', ' 441', ' 159', '2'], ['14025', '369', '403', ' 126', ' 442', ' 159', '2'], ['14026', '369', '403', ' 127', ' 442', ' 160', '2'], ['14027', '369', '404', ' 129', ' 441', ' 161', '2'], ['14028', '369', '406', ' 132', ' 441', ' 162', '2'], ['14029', '369', '405', ' 129', ' 444', ' 163', '2'], ['14030', '369', '406', ' 130', ' 445', ' 164', '2'], ['14031', '369', '407', ' 129', ' 447', ' 165', '2'], ['14032', '369', '408', ' 130', ' 448', ' 165', '2'], ['14033', '369', '408', ' 131', ' 448', ' 166', '2'], ['14034', '369', '408', ' 132', ' 449', ' 167', '2'], ['14035', '369', '409', ' 133', ' 449', ' 168', '2'], ['14036', '369', '412', ' 136', ' 450', ' 168', '2'], ['14037', '369', '412', ' 137', ' 449', ' 169', '2'], ['14038', '369', '412', ' 138', ' 449', ' 170', '2'], ['14039', '369', '413', ' 138', ' 451', ' 171', '2'], ['14040', '369', '413', ' 139', ' 451', ' 171', '2'], ['14041', '369', '413', ' 139', ' 453', ' 173', '2'], ['14042', '369', '413', ' 139', ' 453', ' 174', '2'], ['14043', '369', '414', ' 141', ' 454', ' 175', '2'], ['14044', '369', '415', ' 141', ' 456', ' 176', '2'], ['14045', '369', '417', ' 143', ' 457', ' 177', '2'], ['14046', '369', '417', ' 143', ' 458', ' 178', '2'], ['14047', '369', '418', ' 144', ' 459', ' 179', '2'], ['14048', '369', '419', ' 144', ' 460', ' 179', '2'], ['14049', '369', '418', ' 145', ' 461', ' 181', '2'], ['14050', '369', '419', ' 145', ' 462', ' 182', '2'], ['14051', '369', '420', ' 146', ' 463', ' 183', '2'], ['14052', '369', '420', ' 146', ' 465', ' 184', '2'], ['14053', '369', '421', ' 146', ' 466', ' 185', '2'], ['14054', '369', '422', ' 147', ' 468', ' 187', '2'], ['14055', '369', '422', ' 147', ' 468', ' 188', '2'], ['14056', '369', '422', ' 146', ' 470', ' 189', '2'], ['14057', '369', '424', ' 149', ' 471', ' 190', '2'], ['14058', '369', '425', ' 150', ' 472', ' 191', '2'], ['14059', '369', '426', ' 151', ' 473', ' 192', '2'], ['14060', '369', '427', ' 151', ' 474', ' 194', '2'], ['14061', '369', '428', ' 153', ' 475', ' 195', '2'], ['14062', '369', '429', ' 153', ' 477', ' 197', '2'], ['14063', '369', '429', ' 154', ' 479', ' 199', '2'], ['14064', '369', '431', ' 155', ' 481', ' 200', '2'], ['14065', '369', '431', ' 155', ' 482', ' 202', '2'], ['14066', '369', '432', ' 156', ' 483', ' 204', '2'], ['14067', '369', '434', ' 158', ' 485', ' 205', '2'], ['14068', '369', '436', ' 159', ' 487', ' 206', '2'], ['14069', '369', '438', ' 161', ' 487', ' 207', '2'], ['14070', '369', '439', ' 162', ' 488', ' 208', '2'], ['14071', '369', '440', ' 163', ' 491', ' 210', '2'], ['14072', '369', '440', ' 163', ' 493', ' 211', '2'], ['14073', '369', '440', ' 164', ' 494', ' 213', '2'], ['14074', '369', '441', ' 165', ' 496', ' 215', '2'], ['14075', '369', '441', ' 166', ' 499', ' 219', '2'], ['14076', '369', '441', ' 166', ' 500', ' 220', '2'], ['14077', '369', '443', ' 169', ' 501', ' 222', '2'], ['14078', '369', '444', ' 170', ' 504', ' 225', '2'], ['14079', '369', '445', ' 171', ' 506', ' 227', '2'], ['14080', '369', '447', ' 172', ' 509', ' 228', '2'], ['14081', '369', '451', ' 176', ' 510', ' 229', '2'], ['14082', '369', '451', ' 175', ' 512', ' 231', '2'], ['14083', '369', '453', ' 176', ' 516', ' 235', '2'], ['14084', '369', '454', ' 178', ' 518', ' 237', '2'], ['14085', '369', '454', ' 179', ' 521', ' 239', '2'], ['14086', '369', '457', ' 182', ' 522', ' 242', '2'], ['14087', '369', '458', ' 185', ' 524', ' 246', '2'], ['14088', '369', '459', ' 186', ' 527', ' 248', '2'], ['14089', '369', '463', ' 189', ' 530', ' 251', '2'], ['14090', '369', '464', ' 190', ' 533', ' 253', '2'], ['14091', '369', '468', ' 193', ' 534', ' 254', '2'], ['14092', '369', '469', ' 195', ' 537', ' 257', '2'], ['14093', '369', '470', ' 197', ' 542', ' 262', '2'], ['14094', '369', '471', ' 199', ' 544', ' 264', '2'], ['14095', '369', '472', ' 199', ' 548', ' 268', '2'], ['14096', '369', '472', ' 199', ' 552', ' 271', '2'], ['14097', '369', '477', ' 206', ' 554', ' 274', '2'], ['14098', '369', '478', ' 206', ' 558', ' 277', '2'], ['14099', '369', '478', ' 204', ' 562', ' 279', '2'], ['14100', '369', '486', ' 213', ' 566', ' 284', '2'], ['14101', '369', '482', ' 207', ' 572', ' 288', '2'], ['14102', '369', '482', ' 208', ' 578', ' 293', '2'], ['14103', '369', '484', ' 209', ' 582', ' 297', '2'], ['14104', '369', '488', ' 212', ' 585', ' 299', '2'], ['14105', '369', '491', ' 216', ' 589', ' 305', '2'], ['14106', '369', '494', ' 218', ' 594', ' 308', '2'], ['14107', '369', '496', ' 220', ' 599', ' 313', '2'], ['14108', '369', '498', ' 222', ' 606', ' 319', '2'], ['14109', '369', '501', ' 224', ' 610', ' 323', '2'], ['14110', '369', '504', ' 226', ' 616', ' 328', '2'], ['14111', '369', '508', ' 231', ' 620', ' 334', '2'], ['14112', '369', '511', ' 234', ' 628', ' 341', '2'], ['14113', '369', '515', ' 239', ' 632', ' 347', '2'], ['14114', '369', '518', ' 241', ' 639', ' 353', '2'], ['14115', '369', '521', ' 245', ' 646', ' 360', '2'], ['14116', '369', '527', ' 252', ' 652', ' 367', '2'], ['14117', '369', '530', ' 253', ' 661', ' 375', '2'], ['14118', '369', '534', ' 257', ' 668', ' 381', '2'], ['14119', '369', '538', ' 262', ' 677', ' 392', '2'], ['14120', '369', '541', ' 266', ' 685', ' 401', '2'], ['14121', '369', '546', ' 270', ' 694', ' 409', '2'], ['14122', '369', '552', ' 273', ' 701', ' 414', '2'], ['14123', '369', '560', ' 277', ' 709', ' 416', '2'], ['14124', '369', '573', ' 281', ' 722', ' 417', '2'], ['14125', '369', '582', ' 288', ' 727', ' 418', '2'], ['14126', '369', '589', ' 294', ' 731', ' 417', '2'], ['14127', '369', '596', ' 301', ' 734', ' 418', '2'], ['14128', '369', '603', ' 308', ' 735', ' 416', '2'], ['14129', '369', '612', ' 315', ' 739', ' 416', '2'], ['14130', '369', '620', ' 320', ' 746', ' 416', '2'], ['14131', '369', '628', ' 323', ' 753', ' 415', '2'], ['14132', '369', '637', ' 333', ' 754', ' 415', '2'], ['14133', '369', '646', ' 343', ' 754', ' 415', '2']]}, {'403': [['14464', '403', '366', ' 105', ' 389', ' 119', '2'], ['14465', '403', '366', ' 104', ' 390', ' 119', '2'], ['14466', '403', '365', ' 104', ' 390', ' 119', '2'], ['14467', '403', '366', ' 104', ' 390', ' 119', '2'], ['14468', '403', '367', ' 104', ' 390', ' 119', '2'], ['14469', '403', '367', ' 105', ' 389', ' 119', '2'], ['14470', '403', '367', ' 105', ' 390', ' 118', '2'], ['14471', '403', '367', ' 105', ' 390', ' 118', '2'], ['14472', '403', '368', ' 105', ' 390', ' 118', '2'], ['14477', '403', '369', ' 106', ' 389', ' 119', '2'], ['14478', '403', '369', ' 107', ' 390', ' 119', '2'], ['14479', '403', '369', ' 107', ' 390', ' 119', '2'], ['14482', '403', '370', ' 107', ' 391', ' 119', '2'], ['14483', '403', '370', ' 107', ' 391', ' 120', '2'], ['14484', '403', '370', ' 107', ' 391', ' 120', '2'], ['14485', '403', '370', ' 107', ' 391', ' 119', '2'], ['14486', '403', '370', ' 107', ' 392', ' 119', '2'], ['14487', '403', '370', ' 107', ' 393', ' 120', '2'], ['14488', '403', '370', ' 107', ' 393', ' 120', '2'], ['14489', '403', '369', ' 107', ' 393', ' 121', '2'], ['14490', '403', '369', ' 107', ' 393', ' 121', '2'], ['14491', '403', '369', ' 106', ' 393', ' 121', '2'], ['14496', '403', '369', ' 106', ' 394', ' 120', '2'], ['14497', '403', '369', ' 106', ' 393', ' 120', '2'], ['14498', '403', '370', ' 106', ' 393', ' 120', '2'], ['14499', '403', '370', ' 106', ' 393', ' 120', '2'], ['14500', '403', '370', ' 106', ' 393', ' 120', '2'], ['14501', '403', '370', ' 106', ' 393', ' 120', '2'], ['14502', '403', '370', ' 106', ' 394', ' 121', '2'], ['14513', '403', '370', ' 106', ' 396', ' 122', '2'], ['14514', '403', '369', ' 106', ' 396', ' 122', '2'], ['14515', '403', '369', ' 106', ' 397', ' 123', '2'], ['14516', '403', '369', ' 106', ' 397', ' 123', '2'], ['14517', '403', '369', ' 106', ' 397', ' 124', '2'], ['14518', '403', '367', ' 104', ' 399', ' 124', '2'], ['14519', '403', '367', ' 104', ' 399', ' 124', '2'], ['14520', '403', '368', ' 103', ' 399', ' 125', '2'], ['14521', '403', '368', ' 103', ' 399', ' 125', '2'], ['14522', '403', '370', ' 104', ' 400', ' 125', '2'], ['14523', '403', '371', ' 105', ' 399', ' 125', '2'], ['14524', '403', '371', ' 105', ' 399', ' 125', '2'], ['14525', '403', '373', ' 107', ' 398', ' 125', '2'], ['14526', '403', '373', ' 108', ' 398', ' 125', '2'], ['14527', '403', '373', ' 109', ' 398', ' 126', '2'], ['14528', '403', '373', ' 109', ' 398', ' 126', '2'], ['14529', '403', '373', ' 109', ' 398', ' 126', '2'], ['14530', '403', '374', ' 109', ' 398', ' 126', '2'], ['14531', '403', '374', ' 110', ' 398', ' 126', '2'], ['14532', '403', '375', ' 110', ' 398', ' 126', '2'], ['14533', '403', '375', ' 110', ' 398', ' 126', '2'], ['14534', '403', '375', ' 111', ' 398', ' 126', '2'], ['14535', '403', '374', ' 110', ' 398', ' 127', '2'], ['14536', '403', '374', ' 110', ' 399', ' 127', '2'], ['14537', '403', '374', ' 110', ' 399', ' 127', '2'], ['14538', '403', '374', ' 110', ' 398', ' 127', '2'], ['14539', '403', '374', ' 110', ' 398', ' 127', '2'], ['14540', '403', '374', ' 110', ' 398', ' 127', '2'], ['14541', '403', '374', ' 110', ' 398', ' 127', '2'], ['14546', '403', '377', ' 114', ' 400', ' 130', '2'], ['14547', '403', '376', ' 113', ' 402', ' 131', '2'], ['14548', '403', '375', ' 112', ' 403', ' 132', '2'], ['14549', '403', '374', ' 111', ' 404', ' 132', '2'], ['14550', '403', '375', ' 111', ' 403', ' 132', '2'], ['14551', '403', '375', ' 112', ' 403', ' 132', '2'], ['14553', '403', '374', ' 112', ' 404', ' 133', '2'], ['14554', '403', '375', ' 112', ' 403', ' 133', '2'], ['14555', '403', '375', ' 112', ' 404', ' 133', '2'], ['14557', '403', '374', ' 111', ' 405', ' 133', '2'], ['14558', '403', '374', ' 111', ' 405', ' 134', '2'], ['14559', '403', '376', ' 113', ' 405', ' 134', '2'], ['14560', '403', '376', ' 113', ' 405', ' 134', '2'], ['14561', '403', '376', ' 112', ' 405', ' 134', '2'], ['14562', '403', '377', ' 113', ' 405', ' 134', '2'], ['14563', '403', '377', ' 114', ' 405', ' 134', '2'], ['14564', '403', '377', ' 113', ' 405', ' 134', '2'], ['14565', '403', '377', ' 113', ' 406', ' 134', '2'], ['14566', '403', '377', ' 113', ' 407', ' 135', '2'], ['14567', '403', '378', ' 113', ' 408', ' 135', '2'], ['14568', '403', '378', ' 113', ' 408', ' 135', '2'], ['14569', '403', '378', ' 113', ' 409', ' 135', '2'], ['14570', '403', '378', ' 113', ' 409', ' 136', '2'], ['14571', '403', '378', ' 113', ' 410', ' 136', '2'], ['14572', '403', '378', ' 113', ' 410', ' 137', '2'], ['14573', '403', '378', ' 113', ' 410', ' 137', '2'], ['14574', '403', '377', ' 111', ' 411', ' 137', '2'], ['14575', '403', '377', ' 110', ' 412', ' 137', '2'], ['14576', '403', '377', ' 110', ' 412', ' 137', '2'], ['14577', '403', '377', ' 110', ' 413', ' 138', '2'], ['14578', '403', '377', ' 109', ' 413', ' 138', '2'], ['14579', '403', '378', ' 109', ' 413', ' 138', '2'], ['14580', '403', '379', ' 111', ' 413', ' 138', '2'], ['14581', '403', '380', ' 111', ' 413', ' 139', '2'], ['14582', '403', '381', ' 111', ' 414', ' 139', '2'], ['14583', '403', '381', ' 111', ' 414', ' 139', '2'], ['14584', '403', '382', ' 111', ' 414', ' 139', '2'], ['14585', '403', '381', ' 111', ' 414', ' 139', '2'], ['14586', '403', '382', ' 111', ' 414', ' 139', '2'], ['14587', '403', '382', ' 111', ' 415', ' 139', '2'], ['14588', '403', '382', ' 111', ' 415', ' 139', '2'], ['14589', '403', '383', ' 112', ' 415', ' 139', '2'], ['14599', '403', '385', ' 117', ' 416', ' 143', '2'], ['14600', '403', '387', ' 118', ' 417', ' 144', '2'], ['14601', '403', '388', ' 119', ' 417', ' 144', '2'], ['14604', '403', '389', ' 122', ' 417', ' 145', '2'], ['14607', '403', '389', ' 122', ' 417', ' 145', '2'], ['14608', '403', '389', ' 122', ' 417', ' 145', '2'], ['14609', '403', '388', ' 121', ' 418', ' 145', '2'], ['14610', '403', '389', ' 120', ' 419', ' 146', '2'], ['14611', '403', '389', ' 120', ' 420', ' 146', '2'], ['14612', '403', '390', ' 121', ' 420', ' 147', '2'], ['14613', '403', '390', ' 121', ' 419', ' 147', '2'], ['14614', '403', '390', ' 122', ' 419', ' 147', '2'], ['14615', '403', '390', ' 122', ' 420', ' 147', '2'], ['14616', '403', '390', ' 123', ' 421', ' 148', '2'], ['14617', '403', '391', ' 123', ' 422', ' 148', '2'], ['14618', '403', '392', ' 125', ' 422', ' 149', '2'], ['14619', '403', '392', ' 125', ' 422', ' 150', '2'], ['14620', '403', '391', ' 124', ' 424', ' 150', '2'], ['14621', '403', '391', ' 123', ' 425', ' 151', '2'], ['14622', '403', '391', ' 123', ' 425', ' 151', '2'], ['14623', '403', '392', ' 125', ' 423', ' 151', '2'], ['14624', '403', '392', ' 126', ' 425', ' 151', '2'], ['14625', '403', '393', ' 126', ' 425', ' 152', '2'], ['14626', '403', '392', ' 126', ' 425', ' 152', '2'], ['14627', '403', '393', ' 126', ' 426', ' 152', '2'], ['14628', '403', '393', ' 126', ' 427', ' 152', '2'], ['14629', '403', '393', ' 126', ' 428', ' 153', '2'], ['14630', '403', '393', ' 126', ' 428', ' 154', '2'], ['14631', '403', '393', ' 126', ' 429', ' 154', '2'], ['14632', '403', '393', ' 126', ' 429', ' 155', '2'], ['14633', '403', '394', ' 127', ' 430', ' 156', '2'], ['14634', '403', '395', ' 127', ' 431', ' 156', '2'], ['14635', '403', '396', ' 128', ' 432', ' 157', '2'], ['14636', '403', '395', ' 128', ' 432', ' 157', '2'], ['14637', '403', '396', ' 128', ' 432', ' 158', '2'], ['14638', '403', '396', ' 129', ' 432', ' 158', '2'], ['14639', '403', '396', ' 129', ' 433', ' 158', '2'], ['14640', '403', '397', ' 129', ' 434', ' 159', '2'], ['14641', '403', '398', ' 129', ' 434', ' 159', '2'], ['14642', '403', '398', ' 131', ' 434', ' 159', '2'], ['14643', '403', '399', ' 131', ' 434', ' 160', '2'], ['14644', '403', '398', ' 131', ' 435', ' 160', '2'], ['14645', '403', '399', ' 131', ' 435', ' 161', '2'], ['14646', '403', '399', ' 132', ' 435', ' 161', '2'], ['14647', '403', '400', ' 133', ' 437', ' 163', '2'], ['14648', '403', '400', ' 133', ' 438', ' 163', '2'], ['14649', '403', '399', ' 133', ' 438', ' 164', '2'], ['14650', '403', '399', ' 133', ' 438', ' 165', '2'], ['14651', '403', '399', ' 134', ' 438', ' 165', '2'], ['14652', '403', '401', ' 134', ' 440', ' 166', '2'], ['14653', '403', '401', ' 134', ' 440', ' 166', '2'], ['14654', '403', '400', ' 134', ' 441', ' 167', '2'], ['14655', '403', '401', ' 135', ' 441', ' 168', '2'], ['14656', '403', '400', ' 135', ' 443', ' 169', '2'], ['14657', '403', '400', ' 135', ' 443', ' 170', '2'], ['14658', '403', '401', ' 135', ' 443', ' 170', '2'], ['14659', '403', '403', ' 137', ' 444', ' 171', '2'], ['14660', '403', '403', ' 138', ' 444', ' 171', '2'], ['14661', '403', '402', ' 138', ' 443', ' 171', '2'], ['14662', '403', '402', ' 138', ' 443', ' 172', '2'], ['14663', '403', '403', ' 139', ' 444', ' 172', '2'], ['14664', '403', '405', ' 141', ' 445', ' 173', '2'], ['14665', '403', '405', ' 141', ' 446', ' 173', '2'], ['14666', '403', '406', ' 141', ' 447', ' 174', '2'], ['14667', '403', '406', ' 140', ' 449', ' 175', '2'], ['14668', '403', '405', ' 140', ' 450', ' 176', '2'], ['14669', '403', '406', ' 140', ' 451', ' 177', '2'], ['14670', '403', '407', ' 141', ' 450', ' 177', '2'], ['14671', '403', '407', ' 142', ' 450', ' 177', '2'], ['14672', '403', '407', ' 142', ' 451', ' 178', '2'], ['14673', '403', '407', ' 142', ' 452', ' 179', '2'], ['14674', '403', '408', ' 142', ' 455', ' 181', '2'], ['14675', '403', '409', ' 143', ' 454', ' 181', '2'], ['14676', '403', '408', ' 143', ' 454', ' 181', '2'], ['14677', '403', '409', ' 145', ' 455', ' 184', '2'], ['14678', '403', '409', ' 145', ' 456', ' 185', '2'], ['14679', '403', '409', ' 146', ' 456', ' 186', '2'], ['14680', '403', '410', ' 146', ' 456', ' 186', '2'], ['14681', '403', '411', ' 148', ' 456', ' 187', '2'], ['14682', '403', '411', ' 148', ' 457', ' 187', '2'], ['14683', '403', '412', ' 149', ' 458', ' 188', '2'], ['14684', '403', '413', ' 149', ' 458', ' 189', '2'], ['14685', '403', '412', ' 148', ' 460', ' 190', '2'], ['14686', '403', '412', ' 148', ' 461', ' 191', '2'], ['14687', '403', '413', ' 149', ' 462', ' 192', '2'], ['14688', '403', '413', ' 148', ' 463', ' 192', '2'], ['14689', '403', '413', ' 148', ' 463', ' 193', '2'], ['14690', '403', '414', ' 149', ' 463', ' 193', '2'], ['14691', '403', '415', ' 150', ' 464', ' 194', '2'], ['14692', '403', '414', ' 150', ' 465', ' 197', '2'], ['14693', '403', '414', ' 151', ' 466', ' 198', '2'], ['14694', '403', '414', ' 151', ' 466', ' 199', '2'], ['14695', '403', '415', ' 152', ' 466', ' 200', '2'], ['14696', '403', '416', ' 153', ' 467', ' 201', '2'], ['14697', '403', '417', ' 154', ' 468', ' 201', '2'], ['14698', '403', '417', ' 155', ' 468', ' 202', '2'], ['14699', '403', '419', ' 156', ' 469', ' 203', '2'], ['14700', '403', '418', ' 157', ' 469', ' 205', '2'], ['14701', '403', '419', ' 158', ' 471', ' 206', '2'], ['14702', '403', '420', ' 158', ' 472', ' 207', '2'], ['14703', '403', '420', ' 159', ' 472', ' 208', '2'], ['14704', '403', '421', ' 160', ' 473', ' 209', '2'], ['14705', '403', '421', ' 161', ' 474', ' 211', '2'], ['14706', '403', '422', ' 162', ' 474', ' 211', '2'], ['14707', '403', '422', ' 162', ' 475', ' 212', '2'], ['14708', '403', '422', ' 162', ' 477', ' 213', '2'], ['14709', '403', '423', ' 162', ' 479', ' 216', '2'], ['14710', '403', '423', ' 164', ' 479', ' 217', '2'], ['14711', '403', '424', ' 164', ' 481', ' 219', '2'], ['14712', '403', '425', ' 165', ' 483', ' 221', '2'], ['14713', '403', '425', ' 167', ' 484', ' 223', '2'], ['14714', '403', '427', ' 168', ' 484', ' 223', '2'], ['14715', '403', '427', ' 168', ' 484', ' 223', '2'], ['14716', '403', '427', ' 168', ' 485', ' 224', '2'], ['14717', '403', '427', ' 169', ' 486', ' 226', '2'], ['14718', '403', '428', ' 170', ' 488', ' 228', '2'], ['14719', '403', '429', ' 171', ' 491', ' 230', '2'], ['14720', '403', '429', ' 171', ' 493', ' 232', '2'], ['14721', '403', '430', ' 172', ' 495', ' 233', '2'], ['14722', '403', '430', ' 172', ' 496', ' 235', '2'], ['14723', '403', '430', ' 173', ' 497', ' 236', '2'], ['14724', '403', '432', ' 175', ' 497', ' 236', '2'], ['14725', '403', '432', ' 175', ' 500', ' 239', '2'], ['14726', '403', '431', ' 175', ' 502', ' 242', '2'], ['14727', '403', '432', ' 175', ' 505', ' 243', '2'], ['14728', '403', '434', ' 178', ' 506', ' 247', '2'], ['14729', '403', '436', ' 181', ' 508', ' 249', '2'], ['14730', '403', '437', ' 183', ' 508', ' 250', '2'], ['14731', '403', '437', ' 186', ' 509', ' 253', '2'], ['14732', '403', '438', ' 187', ' 511', ' 255', '2'], ['14733', '403', '441', ' 190', ' 513', ' 256', '2'], ['14734', '403', '439', ' 190', ' 516', ' 260', '2'], ['14735', '403', '441', ' 190', ' 519', ' 261', '2'], ['14736', '403', '440', ' 189', ' 523', ' 265', '2'], ['14737', '403', '441', ' 191', ' 525', ' 269', '2'], ['14738', '403', '442', ' 192', ' 527', ' 270', '2'], ['14739', '403', '443', ' 193', ' 530', ' 274', '2'], ['14740', '403', '446', ' 194', ' 532', ' 275', '2'], ['14741', '403', '447', ' 196', ' 535', ' 278', '2'], ['14742', '403', '449', ' 199', ' 537', ' 281', '2'], ['14743', '403', '450', ' 200', ' 538', ' 282', '2'], ['14744', '403', '451', ' 202', ' 541', ' 285', '2'], ['14745', '403', '450', ' 203', ' 546', ' 292', '2'], ['14746', '403', '452', ' 206', ' 548', ' 296', '2'], ['14747', '403', '455', ' 208', ' 551', ' 297', '2'], ['14748', '403', '457', ' 211', ' 552', ' 299', '2'], ['14749', '403', '459', ' 214', ' 555', ' 303', '2'], ['14750', '403', '460', ' 216', ' 558', ' 306', '2'], ['14751', '403', '461', ' 217', ' 562', ' 310', '2'], ['14752', '403', '463', ' 218', ' 567', ' 313', '2'], ['14753', '403', '464', ' 220', ' 570', ' 317', '2'], ['14754', '403', '466', ' 222', ' 575', ' 322', '2'], ['14755', '403', '468', ' 224', ' 579', ' 325', '2'], ['14756', '403', '470', ' 226', ' 583', ' 330', '2'], ['14757', '403', '472', ' 229', ' 588', ' 334', '2'], ['14758', '403', '474', ' 231', ' 591', ' 338', '2'], ['14759', '403', '476', ' 235', ' 595', ' 344', '2'], ['14760', '403', '479', ' 238', ' 600', ' 348', '2'], ['14761', '403', '482', ' 241', ' 605', ' 354', '2'], ['14762', '403', '484', ' 244', ' 610', ' 359', '2'], ['14763', '403', '485', ' 245', ' 615', ' 364', '2'], ['14764', '403', '487', ' 248', ' 619', ' 369', '2'], ['14765', '403', '490', ' 251', ' 625', ' 376', '2'], ['14766', '403', '493', ' 254', ' 632', ' 383', '2'], ['14767', '403', '496', ' 257', ' 638', ' 389', '2'], ['14768', '403', '499', ' 260', ' 645', ' 397', '2'], ['14769', '403', '501', ' 264', ' 652', ' 406', '2'], ['14770', '403', '505', ' 268', ' 657', ' 412', '2'], ['14771', '403', '510', ' 270', ' 662', ' 414', '2'], ['14772', '403', '515', ' 275', ' 664', ' 415', '2'], ['14773', '403', '521', ' 278', ' 668', ' 416', '2'], ['14774', '403', '525', ' 282', ' 672', ' 416', '2'], ['14775', '403', '533', ' 287', ' 677', ' 416', '2'], ['14776', '403', '540', ' 292', ' 681', ' 416', '2'], ['14777', '403', '544', ' 295', ' 683', ' 414', '2'], ['14778', '403', '550', ' 301', ' 684', ' 413', '2']]}]
violation_coordinates_json=[{'2': [['82', '2', '366', ' 103', ' 394', ' 125', '2'],
   ['83', '2', '366', ' 102', ' 395', ' 126', '2'],
   ['84', '2', '366', ' 103', ' 395', ' 127', '2'],
   ['85', '2', '367', ' 103', ' 395', ' 127', '2'],
   ['86', '2', '367', ' 104', ' 395', ' 127', '2'],
   ['87', '2', '367', ' 103', ' 396', ' 127', '2'],
   ['88', '2', '367', ' 103', ' 396', ' 127', '2'],
   ['89', '2', '367', ' 103', ' 396', ' 127', '2'],
   ['90', '2', '367', ' 103', ' 397', ' 127', '2'],
   ['91', '2', '367', ' 103', ' 398', ' 128', '2'],
   ['92', '2', '367', ' 103', ' 398', ' 128', '2'],
   ['93', '2', '366', ' 104', ' 398', ' 129', '2'],
   ['94', '2', '366', ' 104', ' 398', ' 130', '2'],
   ['95', '2', '367', ' 104', ' 399', ' 130', '2'],
   ['96', '2', '368', ' 105', ' 399', ' 130', '2'],
   ['97', '2', '368', ' 105', ' 399', ' 131', '2'],
   ['98', '2', '369', ' 106', ' 399', ' 131', '2'],
   ['99', '2', '369', ' 106', ' 400', ' 131', '2'],
   ['100', '2', '369', ' 107', ' 401', ' 132', '2'],
   ['101', '2', '370', ' 107', ' 401', ' 133', '2'],
   ['104', '2', '373', ' 110', ' 401', ' 133', '2'],
   ['105', '2', '374', ' 111', ' 401', ' 134', '2'],
   ['106', '2', '372', ' 110', ' 402', ' 134', '2'],
   ['107', '2', '372', ' 109', ' 403', ' 134', '2'],
   ['113', '2', '378', ' 118', ' 404', ' 138', '2'],
   ['114', '2', '379', ' 119', ' 404', ' 139', '2'],
   ['116', '2', '380', ' 118', ' 408', ' 140', '2'],
   ['117', '2', '381', ' 119', ' 408', ' 140', '2'],
   ['118', '2', '381', ' 120', ' 409', ' 141', '2'],
   ['119', '2', '380', ' 117', ' 410', ' 141', '2'],
   ['120', '2', '378', ' 113', ' 413', ' 140', '2'],
   ['121', '2', '379', ' 113', ' 413', ' 140', '2'],
   ['122', '2', '379', ' 114', ' 413', ' 141', '2'],
   ['124', '2', '379', ' 114', ' 414', ' 143', '2'],
   ['125', '2', '380', ' 114', ' 414', ' 144', '2'],
   ['128', '2', '382', ' 118', ' 414', ' 146', '2'],
   ['138', '2', '393', ' 128', ' 421', ' 151', '2'],
   ['141', '2', '394', ' 131', ' 423', ' 154', '2'],
   ['142', '2', '393', ' 131', ' 423', ' 155', '2'],
   ['143', '2', '393', ' 131', ' 424', ' 156', '2'],
   ['145', '2', '393', ' 132', ' 425', ' 157', '2'],
   ['146', '2', '395', ' 132', ' 427', ' 157', '2'],
   ['147', '2', '396', ' 133', ' 427', ' 156', '2'],
   ['148', '2', '396', ' 133', ' 428', ' 158', '2'],
   ['150', '2', '397', ' 135', ' 432', ' 161', '2'],
   ['151', '2', '397', ' 134', ' 434', ' 162', '2'],
   ['152', '2', '397', ' 135', ' 436', ' 164', '2'],
   ['153', '2', '398', ' 136', ' 437', ' 165', '2'],
   ['154', '2', '400', ' 137', ' 438', ' 166', '2'],
   ['155', '2', '402', ' 138', ' 441', ' 167', '2'],
   ['156', '2', '401', ' 138', ' 441', ' 167', '2'],
   ['157', '2', '401', ' 139', ' 442', ' 168', '2'],
   ['158', '2', '402', ' 140', ' 443', ' 169', '2'],
   ['159', '2', '401', ' 141', ' 442', ' 170', '2'],
   ['160', '2', '401', ' 141', ' 443', ' 171', '2'],
   ['161', '2', '401', ' 141', ' 444', ' 172', '2'],
   ['162', '2', '403', ' 143', ' 444', ' 173', '2'],
   ['163', '2', '404', ' 143', ' 445', ' 174', '2'],
   ['164', '2', '406', ' 144', ' 446', ' 174', '2'],
   ['165', '2', '407', ' 145', ' 447', ' 175', '2'],
   ['166', '2', '407', ' 146', ' 449', ' 178', '2'],
   ['167', '2', '407', ' 146', ' 451', ' 179', '2'],
   ['168', '2', '407', ' 146', ' 452', ' 180', '2'],
   ['169', '2', '409', ' 147', ' 454', ' 181', '2'],
   ['170', '2', '409', ' 148', ' 455', ' 183', '2'],
   ['171', '2', '411', ' 149', ' 456', ' 183', '2'],
   ['172', '2', '412', ' 148', ' 458', ' 184', '2'],
   ['173', '2', '413', ' 149', ' 460', ' 185', '2'],
   ['174', '2', '414', ' 150', ' 461', ' 186', '2'],
   ['175', '2', '415', ' 151', ' 462', ' 187', '2'],
   ['176', '2', '416', ' 152', ' 463', ' 188', '2'],
   ['177', '2', '417', ' 153', ' 464', ' 189', '2'],
   ['178', '2', '418', ' 153', ' 466', ' 191', '2'],
   ['179', '2', '419', ' 155', ' 468', ' 193', '2'],
   ['180', '2', '421', ' 157', ' 469', ' 194', '2'],
   ['181', '2', '422', ' 158', ' 471', ' 197', '2'],
   ['182', '2', '422', ' 159', ' 472', ' 198', '2'],
   ['183', '2', '423', ' 160', ' 475', ' 201', '2'],
   ['184', '2', '424', ' 161', ' 477', ' 203', '2'],
   ['185', '2', '425', ' 162', ' 478', ' 204', '2'],
   ['186', '2', '425', ' 163', ' 479', ' 206', '2'],
   ['187', '2', '427', ' 164', ' 480', ' 207', '2'],
   ['188', '2', '427', ' 165', ' 481', ' 208', '2'],
   ['189', '2', '429', ' 168', ' 482', ' 210', '2'],
   ['190', '2', '431', ' 169', ' 483', ' 211', '2'],
   ['191', '2', '432', ' 170', ' 486', ' 213', '2'],
   ['192', '2', '432', ' 171', ' 487', ' 215', '2'],
   ['193', '2', '433', ' 172', ' 490', ' 217', '2'],
   ['194', '2', '435', ' 173', ' 493', ' 219', '2'],
   ['195', '2', '435', ' 175', ' 495', ' 223', '2'],
   ['196', '2', '437', ' 177', ' 496', ' 224', '2'],
   ['197', '2', '439', ' 178', ' 498', ' 226', '2'],
   ['198', '2', '440', ' 179', ' 501', ' 229', '2'],
   ['199', '2', '442', ' 181', ' 504', ' 231', '2'],
   ['200', '2', '442', ' 183', ' 506', ' 235', '2'],
   ['201', '2', '444', ' 185', ' 508', ' 237', '2'],
   ['202', '2', '446', ' 186', ' 511', ' 239', '2'],
   ['203', '2', '446', ' 188', ' 512', ' 242', '2'],
   ['204', '2', '449', ' 192', ' 514', ' 245', '2'],
   ['205', '2', '450', ' 193', ' 518', ' 248', '2'],
   ['206', '2', '452', ' 195', ' 520', ' 250', '2'],
   ['207', '2', '453', ' 197', ' 523', ' 254', '2'],
   ['208', '2', '454', ' 199', ' 526', ' 258', '2'],
   ['209', '2', '456', ' 201', ' 530', ' 261', '2'],
   ['210', '2', '457', ' 202', ' 532', ' 263', '2'],
   ['211', '2', '458', ' 203', ' 535', ' 266', '2'],
   ['212', '2', '458', ' 203', ' 539', ' 271', '2'],
   ['213', '2', '462', ' 208', ' 541', ' 274', '2'],
   ['214', '2', '465', ' 212', ' 544', ' 278', '2'],
   ['215', '2', '466', ' 215', ' 548', ' 283', '2'],
   ['216', '2', '467', ' 216', ' 552', ' 287', '2'],
   ['217', '2', '470', ' 219', ' 555', ' 291', '2'],
   ['218', '2', '472', ' 222', ' 560', ' 296', '2'],
   ['219', '2', '475', ' 225', ' 563', ' 299', '2'],
   ['220', '2', '475', ' 227', ' 567', ' 305', '2'],
   ['221', '2', '478', ' 231', ' 572', ' 310', '2'],
   ['222', '2', '481', ' 234', ' 576', ' 314', '2'],
   ['223', '2', '484', ' 237', ' 581', ' 320', '2'],
   ['224', '2', '488', ' 241', ' 587', ' 324', '2'],
   ['225', '2', '491', ' 245', ' 593', ' 331', '2'],
   ['226', '2', '493', ' 248', ' 598', ' 337', '2'],
   ['227', '2', '496', ' 252', ' 604', ' 344', '2'],
   ['228', '2', '500', ' 256', ' 610', ' 350', '2'],
   ['229', '2', '502', ' 261', ' 616', ' 358', '2'],
   ['230', '2', '506', ' 267', ' 621', ' 364', '2'],
   ['231', '2', '510', ' 271', ' 629', ' 373', '2'],
   ['232', '2', '515', ' 276', ' 638', ' 381', '2'],
   ['233', '2', '519', ' 279', ' 646', ' 389', '2'],
   ['234', '2', '521', ' 284', ' 655', ' 400', '2'],
   ['235', '2', '526', ' 291', ' 662', ' 409', '2'],
   ['236', '2', '534', ' 297', ' 668', ' 413', '2'],
   ['237', '2', '543', ' 305', ' 671', ' 414', '2'],
   ['238', '2', '551', ' 312', ' 676', ' 416', '2'],
   ['239', '2', '560', ' 319', ' 680', ' 416', '2'],
   ['240', '2', '570', ' 323', ' 686', ' 414', '2'],
   ['241', '2', '577', ' 331', ' 687', ' 414', '2'],
   ['242', '2', '591', ' 341', ' 695', ' 414', '2'],
   ['243', '2', '603', ' 350', ' 701', ' 413', '2'],
   ['244', '2', '612', ' 360', ' 700', ' 413', '2']]},
 {'7': [['161', '7', '370', ' 118', ' 396', ' 140', '2'],
   ['162', '7', '370', ' 117', ' 397', ' 140', '2'],
   ['163', '7', '369', ' 117', ' 397', ' 141', '2'],
   ['164', '7', '368', ' 117', ' 398', ' 142', '2'],
   ['165', '7', '369', ' 117', ' 399', ' 143', '2'],
   ['166', '7', '370', ' 118', ' 399', ' 143', '2'],
   ['167', '7', '368', ' 116', ' 400', ' 144', '2'],
   ['170', '7', '369', ' 117', ' 401', ' 146', '2'],
   ['171', '7', '369', ' 118', ' 401', ' 146', '2'],
   ['172', '7', '370', ' 119', ' 401', ' 146', '2'],
   ['176', '7', '370', ' 121', ' 402', ' 150', '2'],
   ['177', '7', '371', ' 123', ' 402', ' 151', '2'],
   ['178', '7', '371', ' 123', ' 403', ' 151', '2'],
   ['179', '7', '372', ' 124', ' 404', ' 152', '2'],
   ['180', '7', '372', ' 125', ' 403', ' 153', '2'],
   ['182', '7', '373', ' 126', ' 404', ' 154', '2'],
   ['183', '7', '374', ' 127', ' 406', ' 155', '2'],
   ['184', '7', '374', ' 128', ' 406', ' 156', '2'],
   ['185', '7', '375', ' 128', ' 407', ' 157', '2'],
   ['186', '7', '374', ' 128', ' 407', ' 158', '2'],
   ['187', '7', '374', ' 128', ' 408', ' 158', '2'],
   ['188', '7', '374', ' 129', ' 408', ' 160', '2'],
   ['189', '7', '374', ' 130', ' 409', ' 161', '2'],
   ['190', '7', '375', ' 131', ' 409', ' 162', '2'],
   ['191', '7', '375', ' 131', ' 411', ' 164', '2'],
   ['192', '7', '375', ' 130', ' 412', ' 165', '2'],
   ['193', '7', '376', ' 131', ' 413', ' 165', '2'],
   ['194', '7', '376', ' 131', ' 415', ' 166', '2'],
   ['195', '7', '376', ' 132', ' 414', ' 168', '2'],
   ['196', '7', '377', ' 134', ' 415', ' 169', '2'],
   ['197', '7', '378', ' 135', ' 415', ' 170', '2'],
   ['198', '7', '378', ' 134', ' 417', ' 171', '2'],
   ['199', '7', '380', ' 137', ' 418', ' 173', '2'],
   ['200', '7', '380', ' 137', ' 419', ' 174', '2'],
   ['201', '7', '382', ' 138', ' 420', ' 175', '2'],
   ['202', '7', '383', ' 138', ' 423', ' 176', '2'],
   ['203', '7', '383', ' 140', ' 423', ' 177', '2'],
   ['204', '7', '385', ' 142', ' 423', ' 179', '2'],
   ['205', '7', '386', ' 143', ' 424', ' 180', '2'],
   ['207', '7', '387', ' 145', ' 427', ' 182', '2'],
   ['209', '7', '389', ' 145', ' 432', ' 186', '2'],
   ['210', '7', '389', ' 145', ' 432', ' 187', '2'],
   ['211', '7', '390', ' 147', ' 435', ' 189', '2'],
   ['212', '7', '392', ' 148', ' 435', ' 190', '2'],
   ['213', '7', '392', ' 147', ' 437', ' 191', '2'],
   ['214', '7', '393', ' 149', ' 439', ' 193', '2'],
   ['215', '7', '393', ' 151', ' 441', ' 196', '2'],
   ['216', '7', '394', ' 151', ' 443', ' 197', '2'],
   ['217', '7', '393', ' 151', ' 445', ' 200', '2'],
   ['218', '7', '396', ' 155', ' 446', ' 202', '2'],
   ['219', '7', '397', ' 157', ' 448', ' 204', '2'],
   ['220', '7', '398', ' 157', ' 451', ' 205', '2'],
   ['221', '7', '400', ' 159', ' 453', ' 208', '2'],
   ['222', '7', '401', ' 159', ' 455', ' 209', '2'],
   ['223', '7', '400', ' 159', ' 457', ' 212', '2'],
   ['224', '7', '401', ' 161', ' 458', ' 214', '2'],
   ['225', '7', '402', ' 161', ' 461', ' 217', '2'],
   ['226', '7', '402', ' 162', ' 463', ' 219', '2'],
   ['227', '7', '404', ' 163', ' 466', ' 221', '2'],
   ['228', '7', '407', ' 166', ' 468', ' 224', '2'],
   ['229', '7', '408', ' 168', ' 470', ' 227', '2'],
   ['230', '7', '409', ' 168', ' 473', ' 229', '2'],
   ['231', '7', '411', ' 170', ' 475', ' 231', '2'],
   ['232', '7', '411', ' 169', ' 480', ' 235', '2'],
   ['233', '7', '413', ' 171', ' 482', ' 237', '2'],
   ['234', '7', '415', ' 173', ' 485', ' 240', '2'],
   ['235', '7', '417', ' 174', ' 487', ' 243', '2'],
   ['236', '7', '420', ' 181', ' 489', ' 248', '2'],
   ['237', '7', '422', ' 185', ' 491', ' 251', '2'],
   ['238', '7', '423', ' 183', ' 496', ' 254', '2'],
   ['239', '7', '425', ' 184', ' 499', ' 257', '2'],
   ['240', '7', '428', ' 189', ' 502', ' 261', '2'],
   ['241', '7', '430', ' 191', ' 506', ' 265', '2'],
   ['242', '7', '432', ' 192', ' 511', ' 269', '2'],
   ['243', '7', '433', ' 194', ' 515', ' 274', '2'],
   ['244', '7', '435', ' 196', ' 518', ' 277', '2'],
   ['245', '7', '438', ' 198', ' 523', ' 280', '2'],
   ['246', '7', '440', ' 199', ' 528', ' 286', '2'],
   ['247', '7', '442', ' 201', ' 533', ' 290', '2'],
   ['248', '7', '445', ' 204', ' 538', ' 295', '2'],
   ['249', '7', '448', ' 207', ' 542', ' 300', '2'],
   ['250', '7', '451', ' 211', ' 546', ' 305', '2'],
   ['251', '7', '453', ' 215', ' 552', ' 311', '2'],
   ['252', '7', '455', ' 217', ' 558', ' 319', '2'],
   ['253', '7', '458', ' 220', ' 564', ' 324', '2'],
   ['254', '7', '462', ' 223', ' 570', ' 330', '2'],
   ['255', '7', '466', ' 226', ' 578', ' 336', '2'],
   ['256', '7', '470', ' 231', ' 584', ' 344', '2'],
   ['257', '7', '474', ' 236', ' 590', ' 351', '2'],
   ['258', '7', '478', ' 240', ' 598', ' 358', '2'],
   ['259', '7', '482', ' 243', ' 608', ' 367', '2'],
   ['260', '7', '485', ' 247', ' 616', ' 376', '2'],
   ['261', '7', '489', ' 251', ' 626', ' 386', '2'],
   ['262', '7', '495', ' 257', ' 636', ' 396', '2'],
   ['263', '7', '501', ' 264', ' 645', ' 407', '2'],
   ['264', '7', '510', ' 271', ' 653', ' 412', '2'],
   ['265', '7', '518', ' 275', ' 660', ' 414', '2'],
   ['266', '7', '528', ' 280', ' 670', ' 415', '2'],
   ['267', '7', '541', ' 286', ' 681', ' 416', '2'],
   ['268', '7', '557', ' 293', ' 696', ' 416', '2'],
   ['271', '7', '576', ' 313', ' 698', ' 415', '2'],
   ['272', '7', '588', ' 324', ' 703', ' 415', '2'],
   ['273', '7', '600', ' 334', ' 708', ' 413', '2'],
   ['274', '7', '612', ' 344', ' 713', ' 413', '2'],
   ['275', '7', '627', ' 355', ' 719', ' 413', '2']]},
 {'40': [['1475', '40', '347', ' 114', ' 368', ' 132', '2'],
   ['1476', '40', '348', ' 114', ' 370', ' 133', '2'],
   ['1477', '40', '348', ' 114', ' 370', ' 133', '2'],
   ['1478', '40', '348', ' 114', ' 370', ' 134', '2'],
   ['1479', '40', '347', ' 114', ' 370', ' 134', '2'],
   ['1480', '40', '347', ' 114', ' 370', ' 134', '2'],
   ['1481', '40', '347', ' 115', ' 370', ' 135', '2'],
   ['1482', '40', '347', ' 116', ' 370', ' 135', '2'],
   ['1483', '40', '347', ' 116', ' 371', ' 136', '2'],
   ['1484', '40', '347', ' 116', ' 371', ' 136', '2'],
   ['1485', '40', '347', ' 116', ' 372', ' 137', '2'],
   ['1486', '40', '347', ' 117', ' 372', ' 137', '2'],
   ['1487', '40', '348', ' 119', ' 372', ' 138', '2'],
   ['1488', '40', '347', ' 119', ' 373', ' 140', '2'],
   ['1489', '40', '347', ' 119', ' 374', ' 140', '2'],
   ['1491', '40', '347', ' 120', ' 374', ' 142', '2'],
   ['1492', '40', '348', ' 121', ' 375', ' 143', '2'],
   ['1493', '40', '346', ' 120', ' 375', ' 144', '2'],
   ['1494', '40', '346', ' 121', ' 375', ' 145', '2'],
   ['1495', '40', '347', ' 121', ' 375', ' 145', '2'],
   ['1496', '40', '348', ' 123', ' 375', ' 146', '2'],
   ['1497', '40', '348', ' 124', ' 375', ' 146', '2'],
   ['1498', '40', '349', ' 126', ' 375', ' 147', '2'],
   ['1499', '40', '350', ' 128', ' 375', ' 148', '2'],
   ['1500', '40', '349', ' 127', ' 377', ' 148', '2'],
   ['1501', '40', '349', ' 127', ' 377', ' 148', '2'],
   ['1502', '40', '348', ' 127', ' 378', ' 150', '2'],
   ['1503', '40', '348', ' 127', ' 378', ' 150', '2'],
   ['1504', '40', '347', ' 127', ' 379', ' 151', '2'],
   ['1505', '40', '347', ' 126', ' 380', ' 152', '2'],
   ['1506', '40', '347', ' 127', ' 380', ' 153', '2'],
   ['1507', '40', '346', ' 128', ' 380', ' 153', '2'],
   ['1508', '40', '347', ' 129', ' 380', ' 154', '2'],
   ['1509', '40', '348', ' 129', ' 380', ' 155', '2'],
   ['1510', '40', '348', ' 130', ' 381', ' 155', '2'],
   ['1511', '40', '348', ' 129', ' 383', ' 156', '2'],
   ['1512', '40', '349', ' 130', ' 384', ' 157', '2'],
   ['1513', '40', '348', ' 131', ' 383', ' 158', '2'],
   ['1514', '40', '348', ' 131', ' 384', ' 159', '2'],
   ['1515', '40', '348', ' 132', ' 385', ' 162', '2'],
   ['1516', '40', '348', ' 133', ' 386', ' 163', '2'],
   ['1517', '40', '349', ' 133', ' 388', ' 164', '2'],
   ['1518', '40', '348', ' 134', ' 388', ' 166', '2'],
   ['1519', '40', '348', ' 135', ' 389', ' 167', '2'],
   ['1520', '40', '346', ' 135', ' 388', ' 168', '2'],
   ['1521', '40', '346', ' 135', ' 388', ' 169', '2'],
   ['1522', '40', '347', ' 135', ' 388', ' 169', '2'],
   ['1523', '40', '346', ' 135', ' 389', ' 170', '2'],
   ['1524', '40', '347', ' 136', ' 389', ' 171', '2'],
   ['1525', '40', '346', ' 135', ' 391', ' 173', '2'],
   ['1526', '40', '348', ' 137', ' 391', ' 175', '2'],
   ['1527', '40', '348', ' 138', ' 392', ' 176', '2'],
   ['1528', '40', '348', ' 140', ' 392', ' 178', '2'],
   ['1529', '40', '349', ' 141', ' 393', ' 180', '2'],
   ['1530', '40', '349', ' 143', ' 393', ' 181', '2'],
   ['1531', '40', '349', ' 144', ' 392', ' 183', '2'],
   ['1532', '40', '349', ' 146', ' 393', ' 184', '2'],
   ['1533', '40', '349', ' 146', ' 394', ' 186', '2'],
   ['1534', '40', '350', ' 149', ' 394', ' 187', '2'],
   ['1535', '40', '351', ' 150', ' 395', ' 188', '2'],
   ['1536', '40', '352', ' 151', ' 396', ' 190', '2'],
   ['1537', '40', '353', ' 153', ' 398', ' 193', '2'],
   ['1538', '40', '354', ' 155', ' 399', ' 195', '2'],
   ['1539', '40', '354', ' 157', ' 400', ' 197', '2'],
   ['1540', '40', '353', ' 156', ' 401', ' 199', '2'],
   ['1541', '40', '354', ' 157', ' 401', ' 200', '2'],
   ['1542', '40', '352', ' 156', ' 402', ' 202', '2'],
   ['1543', '40', '353', ' 159', ' 402', ' 204', '2'],
   ['1544', '40', '353', ' 160', ' 403', ' 206', '2'],
   ['1545', '40', '352', ' 160', ' 405', ' 209', '2'],
   ['1546', '40', '353', ' 162', ' 405', ' 211', '2'],
   ['1547', '40', '352', ' 164', ' 406', ' 214', '2'],
   ['1548', '40', '353', ' 165', ' 408', ' 216', '2'],
   ['1549', '40', '353', ' 166', ' 410', ' 220', '2'],
   ['1550', '40', '354', ' 168', ' 411', ' 223', '2'],
   ['1551', '40', '354', ' 170', ' 412', ' 225', '2'],
   ['1552', '40', '354', ' 171', ' 413', ' 228', '2'],
   ['1553', '40', '356', ' 173', ' 416', ' 231', '2'],
   ['1554', '40', '356', ' 175', ' 418', ' 235', '2'],
   ['1555', '40', '356', ' 177', ' 420', ' 238', '2'],
   ['1556', '40', '356', ' 177', ' 422', ' 242', '2'],
   ['1557', '40', '356', ' 180', ' 424', ' 247', '2'],
   ['1558', '40', '357', ' 182', ' 426', ' 250', '2'],
   ['1559', '40', '359', ' 186', ' 426', ' 252', '2'],
   ['1560', '40', '359', ' 188', ' 429', ' 257', '2'],
   ['1561', '40', '360', ' 192', ' 431', ' 262', '2'],
   ['1562', '40', '360', ' 193', ' 433', ' 265', '2'],
   ['1563', '40', '360', ' 196', ' 436', ' 272', '2'],
   ['1564', '40', '360', ' 198', ' 438', ' 276', '2'],
   ['1565', '40', '362', ' 201', ' 441', ' 279', '2'],
   ['1566', '40', '364', ' 204', ' 444', ' 284', '2'],
   ['1567', '40', '368', ' 214', ' 444', ' 288', '2'],
   ['1568', '40', '365', ' 212', ' 449', ' 296', '2'],
   ['1569', '40', '365', ' 216', ' 450', ' 300', '2'],
   ['1570', '40', '366', ' 219', ' 455', ' 307', '2'],
   ['1571', '40', '368', ' 222', ' 459', ' 312', '2'],
   ['1572', '40', '368', ' 226', ' 463', ' 321', '2'],
   ['1573', '40', '369', ' 230', ' 465', ' 326', '2'],
   ['1574', '40', '369', ' 234', ' 470', ' 335', '2'],
   ['1575', '40', '370', ' 240', ' 475', ' 345', '2'],
   ['1576', '40', '370', ' 244', ' 479', ' 352', '2'],
   ['1577', '40', '371', ' 249', ' 484', ' 361', '2'],
   ['1578', '40', '372', ' 254', ' 490', ' 372', '2'],
   ['1579', '40', '373', ' 260', ' 497', ' 384', '2'],
   ['1580', '40', '373', ' 266', ' 505', ' 399', '2'],
   ['1581', '40', '375', ' 272', ' 509', ' 408', '2'],
   ['1582', '40', '380', ' 279', ' 513', ' 413', '2'],
   ['1583', '40', '385', ' 285', ' 516', ' 415', '2'],
   ['1584', '40', '392', ' 293', ' 520', ' 417', '2'],
   ['1585', '40', '400', ' 301', ' 515', ' 410', '2'],
   ['1586', '40', '407', ' 309', ' 519', ' 411', '2'],
   ['1587', '40', '414', ' 318', ' 523', ' 414', '2'],
   ['1588', '40', '415', ' 325', ' 520', ' 413', '2'],
   ['1589', '40', '422', ' 338', ' 516', ' 413', '2'],
   ['1590', '40', '430', ' 350', ' 515', ' 412', '2']]},
 {'56': [['2362', '56', '350', ' 106', ' 375', ' 128', '2'],
   ['2363', '56', '350', ' 106', ' 375', ' 129', '2'],
   ['2365', '56', '350', ' 107', ' 375', ' 130', '2'],
   ['2369', '56', '352', ' 110', ' 374', ' 131', '2'],
   ['2372', '56', '352', ' 111', ' 375', ' 132', '2'],
   ['2373', '56', '351', ' 110', ' 377', ' 133', '2'],
   ['2374', '56', '351', ' 110', ' 377', ' 134', '2'],
   ['2375', '56', '351', ' 111', ' 377', ' 135', '2'],
   ['2376', '56', '351', ' 110', ' 377', ' 135', '2'],
   ['2377', '56', '350', ' 110', ' 378', ' 136', '2'],
   ['2378', '56', '350', ' 110', ' 379', ' 137', '2'],
   ['2379', '56', '349', ' 110', ' 379', ' 138', '2'],
   ['2380', '56', '350', ' 110', ' 379', ' 139', '2'],
   ['2381', '56', '350', ' 112', ' 378', ' 139', '2'],
   ['2382', '56', '350', ' 112', ' 379', ' 140', '2'],
   ['2383', '56', '351', ' 112', ' 379', ' 141', '2'],
   ['2386', '56', '352', ' 116', ' 378', ' 142', '2'],
   ['2387', '56', '352', ' 117', ' 378', ' 143', '2'],
   ['2388', '56', '351', ' 117', ' 379', ' 144', '2'],
   ['2389', '56', '351', ' 117', ' 379', ' 144', '2'],
   ['2390', '56', '351', ' 117', ' 379', ' 145', '2'],
   ['2391', '56', '350', ' 117', ' 380', ' 145', '2'],
   ['2392', '56', '350', ' 117', ' 380', ' 146', '2'],
   ['2393', '56', '352', ' 123', ' 378', ' 147', '2'],
   ['2394', '56', '350', ' 120', ' 379', ' 147', '2'],
   ['2397', '56', '353', ' 126', ' 379', ' 149', '2'],
   ['2398', '56', '351', ' 124', ' 380', ' 150', '2'],
   ['2399', '56', '352', ' 125', ' 381', ' 151', '2'],
   ['2401', '56', '351', ' 124', ' 382', ' 153', '2'],
   ['2402', '56', '351', ' 126', ' 382', ' 153', '2'],
   ['2403', '56', '351', ' 126', ' 382', ' 154', '2'],
   ['2404', '56', '351', ' 126', ' 383', ' 155', '2'],
   ['2407', '56', '351', ' 128', ' 384', ' 158', '2'],
   ['2409', '56', '350', ' 129', ' 386', ' 160', '2'],
   ['2410', '56', '350', ' 129', ' 387', ' 162', '2'],
   ['2411', '56', '350', ' 130', ' 388', ' 164', '2'],
   ['2412', '56', '350', ' 131', ' 388', ' 165', '2'],
   ['2413', '56', '349', ' 131', ' 389', ' 168', '2'],
   ['2415', '56', '349', ' 133', ' 389', ' 171', '2'],
   ['2417', '56', '349', ' 134', ' 390', ' 172', '2'],
   ['2418', '56', '349', ' 135', ' 390', ' 174', '2'],
   ['2419', '56', '349', ' 136', ' 390', ' 176', '2'],
   ['2421', '56', '349', ' 137', ' 390', ' 177', '2'],
   ['2422', '56', '350', ' 138', ' 391', ' 179', '2'],
   ['2423', '56', '350', ' 140', ' 392', ' 181', '2'],
   ['2424', '56', '349', ' 139', ' 394', ' 183', '2'],
   ['2425', '56', '349', ' 140', ' 393', ' 185', '2'],
   ['2426', '56', '349', ' 140', ' 394', ' 186', '2'],
   ['2427', '56', '349', ' 141', ' 395', ' 188', '2'],
   ['2428', '56', '350', ' 143', ' 396', ' 190', '2'],
   ['2430', '56', '351', ' 146', ' 397', ' 193', '2'],
   ['2432', '56', '351', ' 149', ' 398', ' 197', '2'],
   ['2433', '56', '351', ' 150', ' 399', ' 199', '2'],
   ['2434', '56', '352', ' 151', ' 401', ' 202', '2'],
   ['2435', '56', '352', ' 152', ' 402', ' 204', '2'],
   ['2436', '56', '351', ' 153', ' 402', ' 206', '2'],
   ['2437', '56', '351', ' 154', ' 402', ' 209', '2'],
   ['2438', '56', '352', ' 156', ' 403', ' 211', '2'],
   ['2439', '56', '352', ' 158', ' 404', ' 214', '2'],
   ['2440', '56', '352', ' 160', ' 404', ' 217', '2'],
   ['2442', '56', '352', ' 161', ' 407', ' 221', '2'],
   ['2443', '56', '352', ' 163', ' 408', ' 225', '2'],
   ['2446', '56', '351', ' 167', ' 411', ' 233', '2'],
   ['2447', '56', '352', ' 170', ' 413', ' 237', '2'],
   ['2448', '56', '355', ' 178', ' 413', ' 241', '2'],
   ['2449', '56', '356', ' 181', ' 416', ' 247', '2'],
   ['2450', '56', '356', ' 182', ' 418', ' 250', '2'],
   ['2451', '56', '355', ' 182', ' 421', ' 252', '2'],
   ['2452', '56', '355', ' 186', ' 423', ' 258', '2'],
   ['2453', '56', '356', ' 190', ' 425', ' 262', '2'],
   ['2454', '56', '353', ' 190', ' 426', ' 267', '2'],
   ['2455', '56', '354', ' 200', ' 424', ' 273', '2'],
   ['2456', '56', '357', ' 207', ' 425', ' 277', '2'],
   ['2457', '56', '355', ' 203', ' 429', ' 279', '2'],
   ['2458', '56', '353', ' 201', ' 435', ' 284', '2'],
   ['2459', '56', '352', ' 201', ' 438', ' 289', '2'],
   ['2460', '56', '351', ' 205', ' 442', ' 297', '2'],
   ['2461', '56', '352', ' 207', ' 443', ' 300', '2'],
   ['2462', '56', '352', ' 211', ' 447', ' 309', '2'],
   ['2463', '56', '353', ' 217', ' 449', ' 316', '2'],
   ['2464', '56', '354', ' 219', ' 454', ' 323', '2'],
   ['2465', '56', '360', ' 235', ' 452', ' 330', '2'],
   ['2466', '56', '356', ' 231', ' 461', ' 339', '2'],
   ['2468', '56', '356', ' 239', ' 468', ' 354', '2'],
   ['2469', '56', '353', ' 243', ' 473', ' 367', '2'],
   ['2471', '56', '351', ' 253', ' 481', ' 387', '2'],
   ['2472', '56', '351', ' 259', ' 489', ' 403', '2'],
   ['2473', '56', '353', ' 266', ' 492', ' 411', '2'],
   ['2474', '56', '357', ' 272', ' 495', ' 414', '2'],
   ['2475', '56', '363', ' 278', ' 499', ' 417', '2'],
   ['2479', '56', '381', ' 301', ' 496', ' 415', '2'],
   ['2480', '56', '390', ' 318', ' 492', ' 415', '2']]},
 {'58': [['2798', '58', '354', ' 130', ' 375', ' 148', '2'],
   ['2802', '58', '355', ' 131', ' 381', ' 152', '2'],
   ['2805', '58', '354', ' 128', ' 386', ' 154', '2'],
   ['2806', '58', '354', ' 129', ' 387', ' 156', '2'],
   ['2808', '58', '351', ' 126', ' 389', ' 158', '2'],
   ['2810', '58', '352', ' 127', ' 390', ' 160', '2'],
   ['2811', '58', '353', ' 129', ' 391', ' 161', '2'],
   ['2812', '58', '354', ' 133', ' 390', ' 163', '2'],
   ['2813', '58', '356', ' 133', ' 393', ' 165', '2'],
   ['2814', '58', '356', ' 132', ' 395', ' 165', '2'],
   ['2815', '58', '355', ' 131', ' 396', ' 167', '2'],
   ['2816', '58', '356', ' 131', ' 399', ' 168', '2'],
   ['2817', '58', '355', ' 130', ' 400', ' 170', '2'],
   ['2818', '58', '356', ' 134', ' 399', ' 171', '2'],
   ['2819', '58', '356', ' 134', ' 399', ' 172', '2'],
   ['2820', '58', '357', ' 135', ' 399', ' 173', '2'],
   ['2821', '58', '359', ' 138', ' 399', ' 174', '2'],
   ['2822', '58', '359', ' 137', ' 400', ' 175', '2'],
   ['2823', '58', '360', ' 138', ' 401', ' 176', '2'],
   ['2824', '58', '361', ' 142', ' 401', ' 179', '2'],
   ['2825', '58', '363', ' 145', ' 401', ' 180', '2'],
   ['2826', '58', '362', ' 143', ' 403', ' 182', '2'],
   ['2827', '58', '362', ' 144', ' 404', ' 183', '2'],
   ['2828', '58', '363', ' 144', ' 406', ' 185', '2'],
   ['2829', '58', '363', ' 144', ' 408', ' 187', '2'],
   ['2830', '58', '365', ' 146', ' 409', ' 189', '2'],
   ['2831', '58', '366', ' 148', ' 410', ' 190', '2'],
   ['2832', '58', '368', ' 150', ' 411', ' 192', '2'],
   ['2833', '58', '367', ' 149', ' 413', ' 193', '2'],
   ['2834', '58', '367', ' 150', ' 414', ' 196', '2'],
   ['2835', '58', '368', ' 152', ' 414', ' 198', '2'],
   ['2836', '58', '370', ' 154', ' 415', ' 199', '2'],
   ['2837', '58', '370', ' 154', ' 417', ' 201', '2'],
   ['2838', '58', '371', ' 157', ' 418', ' 204', '2'],
   ['2839', '58', '372', ' 160', ' 420', ' 207', '2'],
   ['2840', '58', '375', ' 163', ' 421', ' 209', '2'],
   ['2841', '58', '374', ' 162', ' 423', ' 211', '2'],
   ['2842', '58', '375', ' 164', ' 425', ' 213', '2'],
   ['2843', '58', '375', ' 164', ' 428', ' 216', '2'],
   ['2844', '58', '374', ' 162', ' 432', ' 220', '2'],
   ['2845', '58', '377', ' 167', ' 433', ' 222', '2'],
   ['2846', '58', '379', ' 170', ' 434', ' 226', '2'],
   ['2847', '58', '379', ' 172', ' 435', ' 228', '2'],
   ['2848', '58', '382', ' 177', ' 437', ' 231', '2'],
   ['2849', '58', '384', ' 179', ' 440', ' 234', '2'],
   ['2850', '58', '385', ' 180', ' 443', ' 237', '2'],
   ['2851', '58', '385', ' 183', ' 444', ' 240', '2'],
   ['2852', '58', '387', ' 185', ' 448', ' 244', '2'],
   ['2853', '58', '385', ' 180', ' 455', ' 249', '2'],
   ['2854', '58', '388', ' 186', ' 457', ' 253', '2'],
   ['2855', '58', '388', ' 183', ' 461', ' 256', '2'],
   ['2856', '58', '393', ' 193', ' 461', ' 260', '2'],
   ['2857', '58', '391', ' 189', ' 467', ' 265', '2'],
   ['2858', '58', '393', ' 193', ' 470', ' 270', '2'],
   ['2859', '58', '397', ' 202', ' 471', ' 275', '2'],
   ['2860', '58', '400', ' 207', ' 475', ' 280', '2'],
   ['2861', '58', '399', ' 203', ' 483', ' 286', '2'],
   ['2862', '58', '398', ' 199', ' 489', ' 290', '2'],
   ['2863', '58', '399', ' 201', ' 493', ' 296', '2'],
   ['2864', '58', '401', ' 203', ' 499', ' 301', '2'],
   ['2865', '58', '403', ' 206', ' 503', ' 308', '2'],
   ['2866', '58', '407', ' 210', ' 508', ' 314', '2'],
   ['2867', '58', '409', ' 214', ' 514', ' 322', '2'],
   ['2868', '58', '413', ' 218', ' 520', ' 329', '2'],
   ['2869', '58', '416', ' 221', ' 526', ' 335', '2'],
   ['2870', '58', '419', ' 224', ' 532', ' 343', '2'],
   ['2871', '58', '423', ' 231', ' 538', ' 351', '2'],
   ['2872', '58', '428', ' 238', ' 545', ' 360', '2'],
   ['2873', '58', '430', ' 242', ' 554', ' 372', '2'],
   ['2874', '58', '434', ' 247', ' 563', ' 382', '2'],
   ['2875', '58', '436', ' 252', ' 575', ' 400', '2'],
   ['2876', '58', '442', ' 258', ' 584', ' 409', '2'],
   ['2877', '58', '450', ' 266', ' 589', ' 413', '2'],
   ['2878', '58', '459', ' 273', ' 596', ' 415', '2'],
   ['2879', '58', '468', ' 279', ' 605', ' 418', '2'],
   ['2880', '58', '482', ' 289', ' 612', ' 416', '2'],
   ['3094', '58', '585', ' 239', ' 632', ' 285', '3'],
   ['3096', '58', '588', ' 232', ' 636', ' 280', '3'],
   ['3099', '58', '602', ' 244', ' 645', ' 288', '3'],
   ['3101', '58', '612', ' 257', ' 652', ' 297', '3'],
   ['3102', '58', '616', ' 261', ' 657', ' 303', '3'],
   ['3103', '58', '620', ' 263', ' 664', ' 308', '3'],
   ['3104', '58', '624', ' 267', ' 669', ' 314', '3'],
   ['3106', '58', '632', ' 274', ' 676', ' 320', '3']]},
 {'84': [['3591', '84', '343', ' 110', ' 366', ' 128', '2'],
   ['3596', '84', '342', ' 112', ' 366', ' 130', '2'],
   ['3597', '84', '343', ' 113', ' 366', ' 131', '2'],
   ['3598', '84', '343', ' 114', ' 366', ' 131', '2'],
   ['3599', '84', '343', ' 113', ' 367', ' 131', '2'],
   ['3600', '84', '343', ' 113', ' 368', ' 132', '2'],
   ['3601', '84', '343', ' 113', ' 368', ' 132', '2'],
   ['3602', '84', '344', ' 114', ' 368', ' 133', '2'],
   ['3603', '84', '344', ' 115', ' 368', ' 134', '2'],
   ['3604', '84', '344', ' 116', ' 368', ' 134', '2'],
   ['3605', '84', '344', ' 117', ' 368', ' 134', '2'],
   ['3606', '84', '345', ' 118', ' 368', ' 135', '2'],
   ['3607', '84', '345', ' 118', ' 369', ' 136', '2'],
   ['3608', '84', '344', ' 119', ' 369', ' 137', '2'],
   ['3609', '84', '344', ' 119', ' 369', ' 137', '2'],
   ['3610', '84', '344', ' 119', ' 369', ' 138', '2'],
   ['3611', '84', '344', ' 120', ' 370', ' 139', '2'],
   ['3612', '84', '344', ' 122', ' 370', ' 140', '2'],
   ['3613', '84', '345', ' 123', ' 370', ' 141', '2'],
   ['3614', '84', '345', ' 123', ' 371', ' 142', '2'],
   ['3615', '84', '344', ' 122', ' 371', ' 142', '2'],
   ['3616', '84', '344', ' 123', ' 372', ' 143', '2'],
   ['3617', '84', '344', ' 123', ' 372', ' 144', '2'],
   ['3618', '84', '344', ' 125', ' 371', ' 145', '2'],
   ['3619', '84', '344', ' 126', ' 371', ' 146', '2'],
   ['3620', '84', '343', ' 126', ' 372', ' 147', '2'],
   ['3621', '84', '344', ' 127', ' 372', ' 147', '2'],
   ['3622', '84', '344', ' 128', ' 372', ' 147', '2'],
   ['3623', '84', '344', ' 128', ' 373', ' 148', '2'],
   ['3624', '84', '344', ' 128', ' 373', ' 148', '2'],
   ['3625', '84', '343', ' 128', ' 374', ' 149', '2'],
   ['3626', '84', '342', ' 128', ' 374', ' 150', '2'],
   ['3627', '84', '342', ' 128', ' 374', ' 151', '2'],
   ['3628', '84', '342', ' 128', ' 376', ' 152', '2'],
   ['3629', '84', '341', ' 128', ' 376', ' 153', '2'],
   ['3630', '84', '342', ' 128', ' 376', ' 154', '2'],
   ['3631', '84', '342', ' 129', ' 376', ' 154', '2'],
   ['3632', '84', '342', ' 130', ' 375', ' 155', '2'],
   ['3633', '84', '342', ' 131', ' 376', ' 155', '2'],
   ['3634', '84', '342', ' 131', ' 376', ' 156', '2'],
   ['3635', '84', '342', ' 131', ' 376', ' 157', '2'],
   ['3636', '84', '342', ' 132', ' 377', ' 158', '2'],
   ['3637', '84', '342', ' 133', ' 378', ' 160', '2'],
   ['3638', '84', '343', ' 135', ' 378', ' 161', '2'],
   ['3639', '84', '342', ' 135', ' 379', ' 163', '2'],
   ['3640', '84', '343', ' 136', ' 379', ' 164', '2'],
   ['3641', '84', '343', ' 137', ' 379', ' 165', '2'],
   ['3642', '84', '342', ' 138', ' 380', ' 166', '2'],
   ['3643', '84', '341', ' 139', ' 378', ' 167', '2'],
   ['3644', '84', '342', ' 140', ' 379', ' 169', '2'],
   ['3645', '84', '341', ' 141', ' 379', ' 170', '2'],
   ['3646', '84', '341', ' 142', ' 380', ' 171', '2'],
   ['3647', '84', '341', ' 142', ' 381', ' 173', '2'],
   ['3648', '84', '342', ' 142', ' 382', ' 173', '2'],
   ['3649', '84', '342', ' 144', ' 382', ' 175', '2'],
   ['3650', '84', '343', ' 145', ' 383', ' 176', '2'],
   ['3651', '84', '343', ' 146', ' 384', ' 178', '2'],
   ['3652', '84', '343', ' 147', ' 383', ' 179', '2'],
   ['3653', '84', '342', ' 148', ' 382', ' 179', '2'],
   ['3654', '84', '343', ' 149', ' 383', ' 180', '2'],
   ['3655', '84', '342', ' 150', ' 385', ' 184', '2'],
   ['3656', '84', '341', ' 149', ' 386', ' 185', '2'],
   ['3657', '84', '341', ' 150', ' 387', ' 187', '2'],
   ['3658', '84', '341', ' 151', ' 388', ' 189', '2'],
   ['3659', '84', '342', ' 153', ' 389', ' 191', '2'],
   ['3660', '84', '342', ' 156', ' 388', ' 193', '2'],
   ['3661', '84', '342', ' 157', ' 389', ' 196', '2'],
   ['3662', '84', '343', ' 159', ' 390', ' 197', '2'],
   ['3663', '84', '344', ' 161', ' 389', ' 199', '2'],
   ['3664', '84', '344', ' 162', ' 390', ' 200', '2'],
   ['3665', '84', '344', ' 163', ' 391', ' 203', '2'],
   ['3666', '84', '344', ' 164', ' 392', ' 205', '2'],
   ['3667', '84', '344', ' 166', ' 393', ' 209', '2'],
   ['3668', '84', '344', ' 167', ' 394', ' 211', '2'],
   ['3669', '84', '344', ' 169', ' 395', ' 213', '2'],
   ['3670', '84', '344', ' 172', ' 394', ' 215', '2'],
   ['3671', '84', '344', ' 173', ' 394', ' 218', '2'],
   ['3672', '84', '344', ' 175', ' 396', ' 222', '2'],
   ['3673', '84', '344', ' 177', ' 397', ' 225', '2'],
   ['3674', '84', '344', ' 179', ' 398', ' 227', '2'],
   ['3675', '84', '344', ' 180', ' 400', ' 230', '2'],
   ['3676', '84', '345', ' 183', ' 401', ' 234', '2'],
   ['3677', '84', '345', ' 185', ' 403', ' 237', '2'],
   ['3678', '84', '346', ' 186', ' 405', ' 240', '2'],
   ['3679', '84', '346', ' 189', ' 406', ' 244', '2'],
   ['3680', '84', '346', ' 192', ' 406', ' 247', '2'],
   ['3681', '84', '344', ' 194', ' 408', ' 252', '2'],
   ['3682', '84', '344', ' 196', ' 410', ' 257', '2'],
   ['3683', '84', '344', ' 199', ' 412', ' 262', '2'],
   ['3684', '84', '343', ' 202', ' 412', ' 266', '2'],
   ['3685', '84', '344', ' 205', ' 415', ' 270', '2'],
   ['3686', '84', '345', ' 208', ' 417', ' 275', '2'],
   ['3687', '84', '346', ' 211', ' 419', ' 279', '2'],
   ['3688', '84', '346', ' 216', ' 420', ' 285', '2'],
   ['3689', '84', '346', ' 219', ' 423', ' 291', '2'],
   ['3690', '84', '345', ' 222', ' 425', ' 297', '2'],
   ['3691', '84', '344', ' 225', ' 427', ' 303', '2'],
   ['3692', '84', '343', ' 229', ' 429', ' 309', '2'],
   ['3693', '84', '345', ' 233', ' 433', ' 316', '2'],
   ['3694', '84', '345', ' 238', ' 436', ' 323', '2'],
   ['3695', '84', '347', ' 242', ' 439', ' 329', '2'],
   ['3696', '84', '347', ' 247', ' 442', ' 337', '2'],
   ['3697', '84', '346', ' 252', ' 446', ' 347', '2'],
   ['3698', '84', '346', ' 257', ' 448', ' 354', '2'],
   ['3699', '84', '347', ' 264', ' 452', ' 364', '2'],
   ['3700', '84', '345', ' 269', ' 455', ' 374', '2'],
   ['3701', '84', '344', ' 275', ' 460', ' 386', '2'],
   ['3702', '84', '342', ' 281', ' 465', ' 399', '2'],
   ['3703', '84', '342', ' 288', ' 468', ' 409', '2'],
   ['3704', '84', '347', ' 296', ' 470', ' 414', '2'],
   ['3705', '84', '351', ' 302', ' 471', ' 415', '2'],
   ['3706', '84', '360', ' 313', ' 472', ' 416', '2'],
   ['3707', '84', '368', ' 322', ' 471', ' 413', '2'],
   ['3708', '84', '374', ' 332', ' 470', ' 413', '2'],
   ['3709', '84', '380', ' 344', ' 467', ' 413', '2'],
   ['3710', '84', '387', ' 356', ' 463', ' 412', '2']]},
 {'79': [['3541', '79', '374', ' 107', ' 396', ' 120', '2'],
   ['3542', '79', '373', ' 107', ' 397', ' 121', '2'],
   ['3547', '79', '373', ' 108', ' 399', ' 123', '2'],
   ['3548', '79', '374', ' 108', ' 399', ' 124', '2'],
   ['3549', '79', '374', ' 108', ' 399', ' 124', '2'],
   ['3550', '79', '373', ' 108', ' 400', ' 124', '2'],
   ['3554', '79', '373', ' 108', ' 400', ' 126', '2'],
   ['3555', '79', '372', ' 108', ' 401', ' 127', '2'],
   ['3556', '79', '373', ' 109', ' 401', ' 126', '2'],
   ['3558', '79', '375', ' 109', ' 402', ' 127', '2'],
   ['3559', '79', '376', ' 110', ' 402', ' 127', '2'],
   ['3560', '79', '377', ' 111', ' 402', ' 127', '2'],
   ['3561', '79', '378', ' 112', ' 402', ' 127', '2'],
   ['3576', '79', '380', ' 113', ' 406', ' 129', '2'],
   ['3577', '79', '381', ' 113', ' 408', ' 130', '2'],
   ['3578', '79', '380', ' 113', ' 409', ' 131', '2'],
   ['3579', '79', '380', ' 113', ' 409', ' 132', '2'],
   ['3580', '79', '381', ' 113', ' 409', ' 132', '2'],
   ['3581', '79', '381', ' 113', ' 410', ' 132', '2'],
   ['3582', '79', '382', ' 113', ' 410', ' 132', '2'],
   ['3583', '79', '383', ' 113', ' 410', ' 132', '2'],
   ['3584', '79', '383', ' 114', ' 411', ' 133', '2'],
   ['3585', '79', '383', ' 114', ' 411', ' 133', '2'],
   ['3586', '79', '384', ' 114', ' 411', ' 133', '2'],
   ['3587', '79', '384', ' 114', ' 411', ' 133', '2'],
   ['3588', '79', '384', ' 114', ' 411', ' 133', '2'],
   ['3589', '79', '385', ' 115', ' 411', ' 133', '2'],
   ['3590', '79', '386', ' 116', ' 411', ' 134', '2'],
   ['3591', '79', '385', ' 116', ' 411', ' 134', '2'],
   ['3592', '79', '386', ' 116', ' 412', ' 135', '2'],
   ['3593', '79', '387', ' 117', ' 412', ' 135', '2'],
   ['3594', '79', '388', ' 117', ' 412', ' 135', '2'],
   ['3595', '79', '388', ' 118', ' 413', ' 136', '2'],
   ['3596', '79', '388', ' 119', ' 414', ' 137', '2'],
   ['3597', '79', '388', ' 119', ' 414', ' 138', '2'],
   ['3598', '79', '388', ' 119', ' 414', ' 138', '2'],
   ['3599', '79', '389', ' 120', ' 414', ' 138', '2'],
   ['3600', '79', '389', ' 120', ' 415', ' 139', '2'],
   ['3601', '79', '389', ' 120', ' 415', ' 139', '2'],
   ['3602', '79', '389', ' 120', ' 417', ' 139', '2'],
   ['3603', '79', '390', ' 120', ' 417', ' 140', '2'],
   ['3604', '79', '390', ' 120', ' 418', ' 140', '2'],
   ['3605', '79', '391', ' 120', ' 418', ' 140', '2'],
   ['3606', '79', '391', ' 121', ' 418', ' 140', '2'],
   ['3607', '79', '391', ' 121', ' 417', ' 140', '2'],
   ['3608', '79', '392', ' 121', ' 417', ' 140', '2'],
   ['3609', '79', '392', ' 121', ' 418', ' 140', '2'],
   ['3610', '79', '391', ' 121', ' 419', ' 141', '2'],
   ['3611', '79', '392', ' 121', ' 421', ' 142', '2'],
   ['3612', '79', '392', ' 121', ' 421', ' 142', '2'],
   ['3613', '79', '393', ' 122', ' 421', ' 143', '2'],
   ['3614', '79', '393', ' 122', ' 421', ' 143', '2'],
   ['3615', '79', '393', ' 122', ' 422', ' 144', '2'],
   ['3616', '79', '394', ' 124', ' 422', ' 145', '2'],
   ['3617', '79', '395', ' 125', ' 423', ' 145', '2'],
   ['3618', '79', '394', ' 125', ' 423', ' 145', '2'],
   ['3619', '79', '395', ' 125', ' 423', ' 146', '2'],
   ['3620', '79', '394', ' 125', ' 424', ' 146', '2'],
   ['3621', '79', '395', ' 125', ' 424', ' 147', '2'],
   ['3622', '79', '395', ' 126', ' 423', ' 147', '2'],
   ['3623', '79', '396', ' 127', ' 424', ' 147', '2'],
   ['3624', '79', '396', ' 127', ' 424', ' 147', '2'],
   ['3625', '79', '396', ' 127', ' 425', ' 147', '2'],
   ['3626', '79', '396', ' 127', ' 425', ' 148', '2'],
   ['3627', '79', '396', ' 128', ' 426', ' 149', '2'],
   ['3628', '79', '396', ' 129', ' 426', ' 150', '2'],
   ['3629', '79', '396', ' 129', ' 427', ' 150', '2'],
   ['3630', '79', '397', ' 129', ' 428', ' 151', '2'],
   ['3631', '79', '397', ' 129', ' 429', ' 151', '2'],
   ['3632', '79', '398', ' 130', ' 429', ' 152', '2'],
   ['3633', '79', '398', ' 131', ' 429', ' 152', '2'],
   ['3634', '79', '399', ' 131', ' 430', ' 152', '2'],
   ['3635', '79', '399', ' 131', ' 431', ' 153', '2'],
   ['3636', '79', '398', ' 130', ' 432', ' 153', '2'],
   ['3637', '79', '399', ' 130', ' 432', ' 153', '2'],
   ['3638', '79', '400', ' 130', ' 432', ' 153', '2'],
   ['3639', '79', '399', ' 131', ' 434', ' 154', '2'],
   ['3640', '79', '399', ' 131', ' 434', ' 155', '2'],
   ['3641', '79', '400', ' 131', ' 434', ' 155', '2'],
   ['3642', '79', '400', ' 132', ' 434', ' 155', '2'],
   ['3643', '79', '401', ' 133', ' 434', ' 156', '2'],
   ['3644', '79', '402', ' 134', ' 434', ' 156', '2'],
   ['3645', '79', '401', ' 133', ' 436', ' 157', '2'],
   ['3646', '79', '401', ' 133', ' 435', ' 157', '2'],
   ['3647', '79', '402', ' 134', ' 436', ' 158', '2'],
   ['3648', '79', '402', ' 135', ' 437', ' 159', '2'],
   ['3649', '79', '403', ' 136', ' 437', ' 159', '2'],
   ['3650', '79', '403', ' 136', ' 438', ' 160', '2'],
   ['3651', '79', '404', ' 136', ' 440', ' 161', '2'],
   ['3652', '79', '403', ' 136', ' 443', ' 163', '2'],
   ['3653', '79', '403', ' 136', ' 444', ' 163', '2'],
   ['3654', '79', '403', ' 136', ' 445', ' 164', '2'],
   ['3655', '79', '404', ' 138', ' 445', ' 165', '2'],
   ['3656', '79', '404', ' 138', ' 444', ' 166', '2'],
   ['3657', '79', '405', ' 139', ' 445', ' 167', '2'],
   ['3658', '79', '406', ' 140', ' 446', ' 167', '2'],
   ['3659', '79', '405', ' 140', ' 446', ' 168', '2'],
   ['3660', '79', '405', ' 140', ' 446', ' 168', '2'],
   ['3661', '79', '406', ' 140', ' 447', ' 169', '2'],
   ['3662', '79', '406', ' 140', ' 447', ' 170', '2'],
   ['3663', '79', '407', ' 140', ' 448', ' 170', '2'],
   ['3664', '79', '407', ' 141', ' 449', ' 171', '2'],
   ['3665', '79', '408', ' 142', ' 450', ' 172', '2'],
   ['3666', '79', '409', ' 143', ' 450', ' 173', '2'],
   ['3667', '79', '409', ' 144', ' 449', ' 173', '2'],
   ['3668', '79', '410', ' 145', ' 448', ' 173', '2'],
   ['3669', '79', '410', ' 146', ' 449', ' 174', '2'],
   ['3670', '79', '410', ' 146', ' 451', ' 175', '2'],
   ['3671', '79', '411', ' 146', ' 452', ' 176', '2'],
   ['3672', '79', '411', ' 147', ' 454', ' 177', '2'],
   ['3673', '79', '411', ' 147', ' 454', ' 178', '2'],
   ['3674', '79', '412', ' 147', ' 457', ' 180', '2'],
   ['3675', '79', '412', ' 147', ' 457', ' 181', '2'],
   ['3676', '79', '412', ' 148', ' 457', ' 182', '2'],
   ['3677', '79', '411', ' 149', ' 457', ' 183', '2'],
   ['3678', '79', '410', ' 149', ' 457', ' 184', '2'],
   ['3679', '79', '411', ' 150', ' 457', ' 184', '2'],
   ['3680', '79', '413', ' 151', ' 457', ' 184', '2'],
   ['3681', '79', '414', ' 152', ' 459', ' 185', '2'],
   ['3682', '79', '414', ' 152', ' 459', ' 186', '2'],
   ['3683', '79', '415', ' 153', ' 460', ' 187', '2'],
   ['3684', '79', '416', ' 154', ' 461', ' 188', '2'],
   ['3685', '79', '416', ' 155', ' 463', ' 190', '2'],
   ['3686', '79', '417', ' 155', ' 463', ' 191', '2'],
   ['3687', '79', '418', ' 157', ' 463', ' 191', '2'],
   ['3688', '79', '418', ' 157', ' 463', ' 192', '2'],
   ['3689', '79', '419', ' 158', ' 464', ' 194', '2'],
   ['3690', '79', '419', ' 159', ' 466', ' 195', '2'],
   ['3691', '79', '420', ' 160', ' 466', ' 197', '2'],
   ['3692', '79', '420', ' 161', ' 467', ' 198', '2'],
   ['3693', '79', '420', ' 161', ' 469', ' 199', '2'],
   ['3694', '79', '420', ' 163', ' 470', ' 202', '2'],
   ['3695', '79', '420', ' 163', ' 471', ' 203', '2'],
   ['3696', '79', '421', ' 164', ' 472', ' 204', '2'],
   ['3697', '79', '421', ' 164', ' 473', ' 205', '2'],
   ['3698', '79', '421', ' 165', ' 474', ' 206', '2'],
   ['3699', '79', '422', ' 166', ' 474', ' 207', '2'],
   ['3700', '79', '423', ' 167', ' 476', ' 209', '2'],
   ['3701', '79', '424', ' 167', ' 478', ' 210', '2'],
   ['3702', '79', '425', ' 169', ' 478', ' 211', '2'],
   ['3703', '79', '426', ' 170', ' 479', ' 212', '2'],
   ['3704', '79', '426', ' 171', ' 480', ' 214', '2'],
   ['3705', '79', '427', ' 173', ' 480', ' 215', '2'],
   ['3706', '79', '426', ' 173', ' 481', ' 217', '2'],
   ['3707', '79', '426', ' 173', ' 481', ' 218', '2'],
   ['3708', '79', '426', ' 175', ' 482', ' 220', '2'],
   ['3709', '79', '427', ' 176', ' 483', ' 222', '2'],
   ['3710', '79', '429', ' 178', ' 486', ' 224', '2'],
   ['3711', '79', '431', ' 179', ' 487', ' 225', '2'],
   ['3712', '79', '431', ' 180', ' 488', ' 227', '2'],
   ['3713', '79', '432', ' 180', ' 490', ' 228', '2'],
   ['3714', '79', '433', ' 181', ' 492', ' 230', '2'],
   ['3715', '79', '433', ' 183', ' 493', ' 232', '2'],
   ['3716', '79', '434', ' 184', ' 494', ' 234', '2'],
   ['3717', '79', '435', ' 186', ' 495', ' 236', '2'],
   ['3718', '79', '436', ' 188', ' 497', ' 238', '2'],
   ['3719', '79', '438', ' 191', ' 499', ' 241', '2'],
   ['3720', '79', '437', ' 191', ' 501', ' 244', '2'],
   ['3721', '79', '438', ' 192', ' 502', ' 246', '2'],
   ['3722', '79', '438', ' 193', ' 505', ' 248', '2'],
   ['3723', '79', '439', ' 195', ' 506', ' 250', '2'],
   ['3724', '79', '440', ' 196', ' 509', ' 253', '2'],
   ['3725', '79', '441', ' 198', ' 510', ' 255', '2'],
   ['3726', '79', '441', ' 200', ' 511', ' 258', '2'],
   ['3727', '79', '441', ' 201', ' 513', ' 260', '2'],
   ['3728', '79', '443', ' 202', ' 515', ' 262', '2'],
   ['3729', '79', '444', ' 204', ' 518', ' 266', '2'],
   ['3730', '79', '444', ' 205', ' 521', ' 270', '2'],
   ['3731', '79', '446', ' 207', ' 524', ' 274', '2'],
   ['3732', '79', '447', ' 210', ' 525', ' 276', '2'],
   ['3733', '79', '449', ' 213', ' 526', ' 278', '2'],
   ['3734', '79', '450', ' 215', ' 529', ' 282', '2'],
   ['3735', '79', '452', ' 218', ' 531', ' 285', '2'],
   ['3736', '79', '453', ' 220', ' 534', ' 289', '2'],
   ['3737', '79', '454', ' 221', ' 537', ' 292', '2'],
   ['3738', '79', '454', ' 223', ' 539', ' 296', '2'],
   ['3739', '79', '456', ' 225', ' 543', ' 300', '2'],
   ['3740', '79', '457', ' 227', ' 545', ' 303', '2'],
   ['3741', '79', '459', ' 230', ' 550', ' 309', '2'],
   ['3742', '79', '462', ' 233', ' 551', ' 311', '2'],
   ['3743', '79', '464', ' 236', ' 554', ' 314', '2'],
   ['3744', '79', '466', ' 240', ' 558', ' 320', '2'],
   ['3745', '79', '468', ' 242', ' 561', ' 323', '2'],
   ['3746', '79', '470', ' 246', ' 565', ' 329', '2'],
   ['3747', '79', '471', ' 249', ' 569', ' 334', '2'],
   ['3748', '79', '474', ' 252', ' 573', ' 338', '2'],
   ['3749', '79', '474', ' 255', ' 578', ' 345', '2'],
   ['3750', '79', '476', ' 258', ' 582', ' 350', '2'],
   ['3751', '79', '479', ' 262', ' 586', ' 355', '2'],
   ['3752', '79', '482', ' 267', ' 590', ' 361', '2'],
   ['3753', '79', '483', ' 270', ' 596', ' 368', '2'],
   ['3754', '79', '486', ' 274', ' 601', ' 374', '2'],
   ['3755', '79', '488', ' 279', ' 607', ' 382', '2'],
   ['3756', '79', '490', ' 282', ' 612', ' 388', '2'],
   ['3757', '79', '491', ' 286', ' 619', ' 398', '2'],
   ['3758', '79', '495', ' 292', ' 625', ' 406', '2'],
   ['3759', '79', '500', ' 296', ' 629', ' 410', '2'],
   ['3760', '79', '505', ' 300', ' 635', ' 414', '2'],
   ['3761', '79', '511', ' 306', ' 638', ' 415', '2'],
   ['3762', '79', '517', ' 312', ' 639', ' 415', '2'],
   ['3763', '79', '527', ' 317', ' 647', ' 416', '2'],
   ['3764', '79', '530', ' 321', ' 649', ' 417', '2'],
   ['3765', '79', '535', ' 327', ' 650', ' 417', '2'],
   ['3766', '79', '539', ' 334', ' 649', ' 415', '2']]},
 {'92': [['3666', '92', '372', ' 109', ' 394', ' 124', '2'],
   ['3667', '92', '372', ' 109', ' 395', ' 125', '2'],
   ['3668', '92', '371', ' 109', ' 395', ' 126', '2'],
   ['3671', '92', '372', ' 109', ' 397', ' 126', '2'],
   ['3672', '92', '373', ' 109', ' 396', ' 126', '2'],
   ['3674', '92', '374', ' 110', ' 397', ' 127', '2'],
   ['3675', '92', '375', ' 110', ' 398', ' 127', '2'],
   ['3676', '92', '375', ' 111', ' 399', ' 127', '2'],
   ['3677', '92', '374', ' 110', ' 400', ' 128', '2'],
   ['3678', '92', '375', ' 110', ' 399', ' 128', '2'],
   ['3679', '92', '375', ' 111', ' 399', ' 128', '2'],
   ['3680', '92', '375', ' 111', ' 399', ' 128', '2'],
   ['3681', '92', '375', ' 111', ' 400', ' 128', '2'],
   ['3682', '92', '376', ' 111', ' 401', ' 129', '2'],
   ['3685', '92', '376', ' 112', ' 402', ' 131', '2'],
   ['3686', '92', '376', ' 113', ' 401', ' 131', '2'],
   ['3687', '92', '377', ' 113', ' 402', ' 131', '2'],
   ['3688', '92', '377', ' 114', ' 401', ' 131', '2'],
   ['3689', '92', '378', ' 115', ' 402', ' 132', '2'],
   ['3690', '92', '378', ' 114', ' 403', ' 132', '2'],
   ['3691', '92', '378', ' 114', ' 404', ' 133', '2'],
   ['3692', '92', '378', ' 114', ' 404', ' 133', '2'],
   ['3693', '92', '379', ' 114', ' 405', ' 133', '2'],
   ['3694', '92', '380', ' 116', ' 405', ' 134', '2'],
   ['3695', '92', '380', ' 118', ' 404', ' 134', '2'],
   ['3696', '92', '381', ' 118', ' 404', ' 134', '2'],
   ['3697', '92', '381', ' 118', ' 405', ' 134', '2'],
   ['3698', '92', '381', ' 118', ' 406', ' 135', '2'],
   ['3699', '92', '381', ' 118', ' 406', ' 135', '2'],
   ['3700', '92', '381', ' 118', ' 407', ' 135', '2'],
   ['3701', '92', '381', ' 117', ' 408', ' 135', '2'],
   ['3702', '92', '381', ' 118', ' 408', ' 136', '2'],
   ['3703', '92', '381', ' 118', ' 409', ' 137', '2'],
   ['3704', '92', '381', ' 118', ' 409', ' 137', '2'],
   ['3705', '92', '382', ' 118', ' 409', ' 137', '2'],
   ['3706', '92', '382', ' 119', ' 410', ' 137', '2'],
   ['3707', '92', '382', ' 118', ' 410', ' 137', '2'],
   ['3708', '92', '382', ' 118', ' 411', ' 137', '2'],
   ['3709', '92', '382', ' 118', ' 411', ' 138', '2'],
   ['3710', '92', '383', ' 118', ' 412', ' 138', '2'],
   ['3711', '92', '383', ' 118', ' 412', ' 139', '2'],
   ['3712', '92', '384', ' 119', ' 412', ' 139', '2'],
   ['3713', '92', '384', ' 120', ' 412', ' 139', '2'],
   ['3714', '92', '385', ' 120', ' 412', ' 139', '2'],
   ['3715', '92', '385', ' 121', ' 411', ' 140', '2'],
   ['3716', '92', '385', ' 120', ' 412', ' 140', '2'],
   ['3717', '92', '385', ' 121', ' 412', ' 141', '2'],
   ['3718', '92', '385', ' 121', ' 412', ' 142', '2'],
   ['3719', '92', '385', ' 121', ' 413', ' 142', '2'],
   ['3720', '92', '386', ' 122', ' 413', ' 143', '2'],
   ['3721', '92', '387', ' 123', ' 413', ' 144', '2'],
   ['3722', '92', '387', ' 123', ' 414', ' 144', '2'],
   ['3723', '92', '387', ' 122', ' 415', ' 144', '2'],
   ['3724', '92', '387', ' 123', ' 415', ' 145', '2'],
   ['3725', '92', '386', ' 123', ' 415', ' 146', '2'],
   ['3726', '92', '387', ' 123', ' 415', ' 146', '2'],
   ['3727', '92', '388', ' 124', ' 416', ' 146', '2'],
   ['3728', '92', '389', ' 125', ' 416', ' 147', '2'],
   ['3729', '92', '390', ' 126', ' 416', ' 147', '2'],
   ['3730', '92', '390', ' 127', ' 416', ' 147', '2'],
   ['3731', '92', '391', ' 128', ' 418', ' 149', '2'],
   ['3732', '92', '390', ' 128', ' 419', ' 150', '2'],
   ['3733', '92', '390', ' 128', ' 419', ' 151', '2'],
   ['3734', '92', '390', ' 129', ' 421', ' 152', '2'],
   ['3735', '92', '391', ' 130', ' 422', ' 153', '2'],
   ['3736', '92', '391', ' 129', ' 424', ' 154', '2'],
   ['3737', '92', '391', ' 129', ' 423', ' 154', '2'],
   ['3738', '92', '391', ' 129', ' 424', ' 154', '2'],
   ['3739', '92', '391', ' 130', ' 424', ' 155', '2'],
   ['3740', '92', '391', ' 130', ' 424', ' 155', '2'],
   ['3741', '92', '391', ' 130', ' 424', ' 156', '2'],
   ['3742', '92', '392', ' 131', ' 425', ' 157', '2'],
   ['3743', '92', '393', ' 132', ' 425', ' 157', '2'],
   ['3744', '92', '393', ' 133', ' 425', ' 158', '2'],
   ['3745', '92', '393', ' 134', ' 424', ' 159', '2'],
   ['3746', '92', '393', ' 135', ' 425', ' 160', '2'],
   ['3747', '92', '394', ' 135', ' 426', ' 160', '2'],
   ['3748', '92', '395', ' 135', ' 428', ' 161', '2'],
   ['3749', '92', '396', ' 136', ' 429', ' 162', '2'],
   ['3750', '92', '396', ' 136', ' 431', ' 163', '2'],
   ['3751', '92', '396', ' 137', ' 433', ' 165', '2'],
   ['3752', '92', '395', ' 137', ' 432', ' 166', '2'],
   ['3753', '92', '396', ' 138', ' 434', ' 167', '2'],
   ['3754', '92', '396', ' 139', ' 435', ' 168', '2'],
   ['3755', '92', '397', ' 140', ' 435', ' 168', '2'],
   ['3756', '92', '398', ' 140', ' 437', ' 169', '2'],
   ['3757', '92', '399', ' 141', ' 439', ' 171', '2'],
   ['3758', '92', '399', ' 142', ' 439', ' 172', '2'],
   ['3759', '92', '398', ' 143', ' 439', ' 173', '2'],
   ['3760', '92', '399', ' 142', ' 440', ' 173', '2'],
   ['3761', '92', '399', ' 143', ' 439', ' 173', '2'],
   ['3762', '92', '400', ' 143', ' 439', ' 173', '2'],
   ['3763', '92', '400', ' 144', ' 439', ' 174', '2'],
   ['3764', '92', '401', ' 145', ' 441', ' 176', '2'],
   ['3765', '92', '401', ' 146', ' 440', ' 177', '2'],
   ['3766', '92', '400', ' 147', ' 440', ' 179', '2'],
   ['3767', '92', '401', ' 148', ' 441', ' 179', '2'],
   ['3768', '92', '402', ' 148', ' 442', ' 180', '2'],
   ['3769', '92', '402', ' 148', ' 444', ' 181', '2'],
   ['3770', '92', '404', ' 149', ' 445', ' 182', '2'],
   ['3771', '92', '404', ' 149', ' 445', ' 183', '2'],
   ['3772', '92', '404', ' 149', ' 447', ' 185', '2'],
   ['3773', '92', '406', ' 151', ' 447', ' 185', '2'],
   ['3774', '92', '407', ' 153', ' 448', ' 186', '2'],
   ['3775', '92', '408', ' 154', ' 449', ' 188', '2'],
   ['3776', '92', '409', ' 155', ' 450', ' 189', '2'],
   ['3777', '92', '409', ' 156', ' 451', ' 191', '2'],
   ['3778', '92', '411', ' 158', ' 452', ' 192', '2'],
   ['3779', '92', '412', ' 158', ' 454', ' 194', '2'],
   ['3780', '92', '413', ' 160', ' 456', ' 196', '2'],
   ['3781', '92', '414', ' 161', ' 457', ' 198', '2'],
   ['3782', '92', '414', ' 161', ' 458', ' 199', '2'],
   ['3783', '92', '414', ' 162', ' 459', ' 202', '2'],
   ['3784', '92', '415', ' 163', ' 461', ' 203', '2'],
   ['3785', '92', '415', ' 164', ' 463', ' 205', '2'],
   ['3786', '92', '417', ' 165', ' 464', ' 206', '2'],
   ['3787', '92', '418', ' 165', ' 467', ' 208', '2'],
   ['3788', '92', '420', ' 167', ' 467', ' 210', '2'],
   ['3789', '92', '421', ' 169', ' 469', ' 212', '2'],
   ['3790', '92', '422', ' 171', ' 470', ' 214', '2'],
   ['3791', '92', '422', ' 173', ' 470', ' 216', '2'],
   ['3792', '92', '423', ' 174', ' 471', ' 218', '2'],
   ['3793', '92', '423', ' 175', ' 474', ' 222', '2'],
   ['3794', '92', '424', ' 177', ' 475', ' 223', '2'],
   ['3795', '92', '426', ' 179', ' 477', ' 226', '2'],
   ['3796', '92', '427', ' 179', ' 479', ' 228', '2'],
   ['3797', '92', '428', ' 181', ' 481', ' 230', '2'],
   ['3798', '92', '430', ' 182', ' 484', ' 233', '2'],
   ['3799', '92', '432', ' 185', ' 486', ' 236', '2'],
   ['3800', '92', '433', ' 188', ' 487', ' 238', '2'],
   ['3801', '92', '433', ' 189', ' 490', ' 243', '2'],
   ['3802', '92', '434', ' 190', ' 494', ' 245', '2'],
   ['3803', '92', '436', ' 193', ' 494', ' 248', '2'],
   ['3804', '92', '436', ' 193', ' 497', ' 251', '2'],
   ['3805', '92', '437', ' 195', ' 500', ' 254', '2'],
   ['3806', '92', '438', ' 197', ' 503', ' 258', '2'],
   ['3807', '92', '439', ' 200', ' 504', ' 261', '2'],
   ['3808', '92', '442', ' 202', ' 508', ' 264', '2'],
   ['3809', '92', '442', ' 204', ' 510', ' 268', '2'],
   ['3810', '92', '444', ' 206', ' 513', ' 272', '2'],
   ['3811', '92', '445', ' 209', ' 515', ' 275', '2'],
   ['3812', '92', '447', ' 213', ' 517', ' 280', '2'],
   ['3813', '92', '449', ' 216', ' 519', ' 284', '2'],
   ['3814', '92', '450', ' 218', ' 522', ' 287', '2'],
   ['3815', '92', '451', ' 221', ' 527', ' 294', '2'],
   ['3816', '92', '453', ' 224', ' 530', ' 298', '2'],
   ['3817', '92', '455', ' 227', ' 533', ' 301', '2'],
   ['3818', '92', '457', ' 230', ' 536', ' 306', '2'],
   ['3819', '92', '459', ' 234', ' 540', ' 312', '2'],
   ['3820', '92', '461', ' 237', ' 545', ' 318', '2'],
   ['3821', '92', '463', ' 241', ' 549', ' 323', '2'],
   ['3822', '92', '466', ' 245', ' 554', ' 330', '2'],
   ['3823', '92', '468', ' 249', ' 560', ' 337', '2'],
   ['3824', '92', '470', ' 252', ' 564', ' 343', '2'],
   ['3825', '92', '473', ' 257', ' 567', ' 349', '2'],
   ['3826', '92', '476', ' 262', ' 573', ' 356', '2'],
   ['3827', '92', '479', ' 267', ' 577', ' 363', '2'],
   ['3828', '92', '481', ' 271', ' 584', ' 372', '2'],
   ['3829', '92', '482', ' 275', ' 591', ' 381', '2'],
   ['3830', '92', '486', ' 280', ' 596', ' 388', '2'],
   ['3831', '92', '488', ' 286', ' 603', ' 399', '2'],
   ['3832', '92', '493', ' 292', ' 609', ' 407', '2'],
   ['3833', '92', '498', ' 299', ' 613', ' 412', '2'],
   ['3834', '92', '504', ' 305', ' 618', ' 415', '2'],
   ['3835', '92', '513', ' 312', ' 623', ' 416', '2'],
   ['3836', '92', '521', ' 317', ' 628', ' 415', '2'],
   ['3837', '92', '527', ' 324', ' 627', ' 412', '2'],
   ['3838', '92', '533', ' 333', ' 630', ' 414', '2'],
   ['3839', '92', '541', ' 343', ' 631', ' 413', '2']]},
 {'101': [['4118', '101', '357', ' 105', ' 382', ' 123', '2'],
   ['4119', '101', '357', ' 106', ' 382', ' 124', '2'],
   ['4120', '101', '358', ' 107', ' 383', ' 125', '2'],
   ['4121', '101', '357', ' 106', ' 383', ' 125', '2'],
   ['4122', '101', '357', ' 106', ' 384', ' 125', '2'],
   ['4123', '101', '357', ' 106', ' 384', ' 125', '2'],
   ['4124', '101', '357', ' 106', ' 385', ' 125', '2'],
   ['4125', '101', '358', ' 106', ' 384', ' 126', '2'],
   ['4126', '101', '358', ' 106', ' 385', ' 126', '2'],
   ['4127', '101', '357', ' 106', ' 386', ' 126', '2'],
   ['4128', '101', '357', ' 106', ' 386', ' 127', '2'],
   ['4129', '101', '357', ' 106', ' 386', ' 127', '2'],
   ['4130', '101', '358', ' 106', ' 386', ' 127', '2'],
   ['4131', '101', '358', ' 106', ' 387', ' 127', '2'],
   ['4132', '101', '359', ' 106', ' 386', ' 127', '2'],
   ['4133', '101', '358', ' 106', ' 386', ' 127', '2'],
   ['4134', '101', '358', ' 105', ' 387', ' 128', '2'],
   ['4135', '101', '357', ' 104', ' 388', ' 129', '2'],
   ['4136', '101', '357', ' 103', ' 388', ' 129', '2'],
   ['4137', '101', '357', ' 103', ' 389', ' 129', '2'],
   ['4138', '101', '358', ' 103', ' 389', ' 129', '2'],
   ['4139', '101', '358', ' 103', ' 389', ' 130', '2'],
   ['4140', '101', '358', ' 102', ' 389', ' 130', '2'],
   ['4141', '101', '357', ' 101', ' 389', ' 130', '2'],
   ['4142', '101', '358', ' 101', ' 389', ' 131', '2'],
   ['4143', '101', '358', ' 102', ' 389', ' 131', '2'],
   ['4144', '101', '361', ' 106', ' 387', ' 132', '2'],
   ['4145', '101', '361', ' 105', ' 388', ' 132', '2'],
   ['4146', '101', '361', ' 105', ' 389', ' 132', '2'],
   ['4147', '101', '361', ' 103', ' 390', ' 133', '2'],
   ['4149', '101', '363', ' 107', ' 389', ' 133', '2'],
   ['4150', '101', '363', ' 107', ' 389', ' 134', '2'],
   ['4151', '101', '364', ' 110', ' 388', ' 134', '2'],
   ['4152', '101', '365', ' 111', ' 388', ' 134', '2'],
   ['4153', '101', '365', ' 112', ' 388', ' 134', '2'],
   ['4154', '101', '365', ' 113', ' 388', ' 135', '2'],
   ['4155', '101', '366', ' 114', ' 389', ' 136', '2'],
   ['4156', '101', '366', ' 115', ' 389', ' 137', '2'],
   ['4157', '101', '366', ' 116', ' 390', ' 138', '2'],
   ['4158', '101', '366', ' 117', ' 390', ' 138', '2'],
   ['4159', '101', '366', ' 119', ' 390', ' 139', '2'],
   ['4160', '101', '366', ' 119', ' 390', ' 140', '2'],
   ['4161', '101', '366', ' 118', ' 392', ' 140', '2'],
   ['4162', '101', '366', ' 119', ' 391', ' 141', '2'],
   ['4163', '101', '367', ' 120', ' 392', ' 141', '2'],
   ['4166', '101', '367', ' 120', ' 394', ' 142', '2'],
   ['4167', '101', '367', ' 120', ' 394', ' 143', '2'],
   ['4168', '101', '366', ' 119', ' 395', ' 143', '2'],
   ['4169', '101', '366', ' 120', ' 395', ' 144', '2'],
   ['4170', '101', '366', ' 120', ' 395', ' 144', '2'],
   ['4171', '101', '366', ' 121', ' 396', ' 145', '2'],
   ['4172', '101', '366', ' 122', ' 396', ' 146', '2'],
   ['4173', '101', '367', ' 122', ' 397', ' 147', '2'],
   ['4174', '101', '367', ' 122', ' 398', ' 147', '2'],
   ['4175', '101', '367', ' 122', ' 398', ' 147', '2'],
   ['4176', '101', '368', ' 124', ' 397', ' 148', '2'],
   ['4177', '101', '368', ' 124', ' 398', ' 148', '2'],
   ['4178', '101', '368', ' 125', ' 398', ' 149', '2'],
   ['4179', '101', '368', ' 126', ' 398', ' 150', '2'],
   ['4180', '101', '368', ' 126', ' 398', ' 151', '2'],
   ['4181', '101', '368', ' 127', ' 399', ' 151', '2'],
   ['4182', '101', '369', ' 127', ' 400', ' 152', '2'],
   ['4183', '101', '369', ' 127', ' 400', ' 152', '2'],
   ['4184', '101', '370', ' 128', ' 400', ' 153', '2'],
   ['4185', '101', '370', ' 129', ' 401', ' 153', '2'],
   ['4186', '101', '369', ' 128', ' 402', ' 154', '2'],
   ['4187', '101', '369', ' 128', ' 403', ' 155', '2'],
   ['4188', '101', '369', ' 128', ' 403', ' 155', '2'],
   ['4189', '101', '370', ' 128', ' 404', ' 156', '2'],
   ['4190', '101', '370', ' 129', ' 404', ' 157', '2'],
   ['4191', '101', '370', ' 129', ' 405', ' 158', '2'],
   ['4192', '101', '369', ' 130', ' 406', ' 160', '2'],
   ['4193', '101', '370', ' 130', ' 406', ' 161', '2'],
   ['4194', '101', '370', ' 130', ' 407', ' 161', '2'],
   ['4195', '101', '371', ' 131', ' 408', ' 162', '2'],
   ['4196', '101', '371', ' 132', ' 409', ' 164', '2'],
   ['4197', '101', '371', ' 132', ' 410', ' 165', '2'],
   ['4198', '101', '372', ' 133', ' 411', ' 166', '2'],
   ['4199', '101', '372', ' 134', ' 411', ' 167', '2'],
   ['4200', '101', '372', ' 135', ' 411', ' 168', '2'],
   ['4201', '101', '372', ' 135', ' 412', ' 170', '2'],
   ['4202', '101', '372', ' 135', ' 412', ' 170', '2'],
   ['4203', '101', '372', ' 136', ' 413', ' 171', '2'],
   ['4204', '101', '373', ' 136', ' 414', ' 172', '2'],
   ['4205', '101', '373', ' 136', ' 414', ' 173', '2'],
   ['4206', '101', '374', ' 138', ' 415', ' 174', '2'],
   ['4207', '101', '375', ' 140', ' 415', ' 175', '2'],
   ['4208', '101', '376', ' 141', ' 416', ' 177', '2'],
   ['4209', '101', '375', ' 141', ' 417', ' 178', '2'],
   ['4210', '101', '375', ' 142', ' 418', ' 179', '2'],
   ['4211', '101', '376', ' 144', ' 417', ' 180', '2'],
   ['4212', '101', '376', ' 145', ' 418', ' 182', '2'],
   ['4213', '101', '377', ' 147', ' 418', ' 183', '2'],
   ['4214', '101', '378', ' 148', ' 419', ' 184', '2'],
   ['4215', '101', '378', ' 148', ' 421', ' 185', '2'],
   ['4216', '101', '379', ' 149', ' 422', ' 186', '2'],
   ['4217', '101', '379', ' 151', ' 422', ' 188', '2'],
   ['4218', '101', '379', ' 151', ' 424', ' 190', '2'],
   ['4219', '101', '381', ' 152', ' 425', ' 190', '2'],
   ['4220', '101', '382', ' 153', ' 426', ' 191', '2'],
   ['4221', '101', '382', ' 154', ' 428', ' 194', '2'],
   ['4222', '101', '381', ' 154', ' 430', ' 197', '2'],
   ['4223', '101', '382', ' 155', ' 431', ' 198', '2'],
   ['4224', '101', '381', ' 156', ' 432', ' 201', '2'],
   ['4225', '101', '382', ' 156', ' 434', ' 203', '2'],
   ['4226', '101', '383', ' 158', ' 435', ' 205', '2'],
   ['4227', '101', '385', ' 161', ' 435', ' 206', '2'],
   ['4228', '101', '385', ' 161', ' 436', ' 207', '2'],
   ['4229', '101', '386', ' 162', ' 438', ' 209', '2'],
   ['4230', '101', '387', ' 162', ' 440', ' 211', '2'],
   ['4231', '101', '388', ' 164', ' 441', ' 213', '2'],
   ['4232', '101', '387', ' 165', ' 442', ' 216', '2'],
   ['4233', '101', '387', ' 166', ' 443', ' 218', '2'],
   ['4234', '101', '388', ' 166', ' 445', ' 221', '2'],
   ['4235', '101', '389', ' 168', ' 447', ' 223', '2'],
   ['4236', '101', '390', ' 170', ' 449', ' 226', '2'],
   ['4237', '101', '390', ' 171', ' 449', ' 227', '2'],
   ['4238', '101', '393', ' 173', ' 451', ' 229', '2'],
   ['4239', '101', '394', ' 175', ' 454', ' 232', '2'],
   ['4240', '101', '394', ' 176', ' 457', ' 236', '2'],
   ['4241', '101', '394', ' 177', ' 458', ' 239', '2'],
   ['4242', '101', '395', ' 179', ' 460', ' 242', '2'],
   ['4243', '101', '396', ' 182', ' 462', ' 245', '2'],
   ['4244', '101', '396', ' 183', ' 465', ' 249', '2'],
   ['4245', '101', '399', ' 186', ' 467', ' 252', '2'],
   ['4246', '101', '399', ' 188', ' 469', ' 255', '2'],
   ['4247', '101', '400', ' 190', ' 472', ' 260', '2'],
   ['4248', '101', '401', ' 192', ' 475', ' 264', '2'],
   ['4249', '101', '403', ' 195', ' 478', ' 268', '2'],
   ['4250', '101', '405', ' 198', ' 481', ' 271', '2'],
   ['4251', '101', '405', ' 201', ' 483', ' 276', '2'],
   ['4252', '101', '406', ' 203', ' 486', ' 281', '2'],
   ['4253', '101', '406', ' 206', ' 490', ' 286', '2'],
   ['4254', '101', '407', ' 208', ' 493', ' 291', '2'],
   ['4255', '101', '409', ' 211', ' 497', ' 297', '2'],
   ['4256', '101', '411', ' 214', ' 500', ' 300', '2'],
   ['4257', '101', '412', ' 217', ' 503', ' 306', '2'],
   ['4258', '101', '415', ' 221', ' 508', ' 312', '2'],
   ['4259', '101', '416', ' 224', ' 514', ' 320', '2'],
   ['4260', '101', '417', ' 228', ' 517', ' 326', '2'],
   ['4261', '101', '419', ' 232', ' 521', ' 332', '2'],
   ['4262', '101', '422', ' 236', ' 525', ' 337', '2'],
   ['4263', '101', '424', ' 241', ' 531', ' 346', '2'],
   ['4264', '101', '427', ' 244', ' 537', ' 353', '2'],
   ['4265', '101', '429', ' 249', ' 543', ' 361', '2'],
   ['4266', '101', '431', ' 254', ' 551', ' 373', '2'],
   ['4267', '101', '433', ' 259', ' 557', ' 382', '2'],
   ['4268', '101', '435', ' 265', ' 568', ' 396', '2'],
   ['4269', '101', '438', ' 270', ' 576', ' 406', '2'],
   ['4270', '101', '443', ' 276', ' 580', ' 411', '2'],
   ['4271', '101', '449', ' 282', ' 585', ' 416', '2'],
   ['4272', '101', '456', ' 290', ' 590', ' 420', '2'],
   ['4273', '101', '468', ' 297', ' 597', ' 418', '2']]},
 {'102': [['4219', '102', '364', ' 106', ' 384', ' 119', '2'],
   ['4220', '102', '364', ' 106', ' 384', ' 120', '2'],
   ['4221', '102', '365', ' 107', ' 385', ' 120', '2'],
   ['4222', '102', '365', ' 107', ' 385', ' 121', '2'],
   ['4223', '102', '365', ' 107', ' 386', ' 121', '2'],
   ['4224', '102', '364', ' 106', ' 386', ' 121', '2'],
   ['4225', '102', '364', ' 107', ' 386', ' 122', '2'],
   ['4226', '102', '363', ' 107', ' 386', ' 122', '2'],
   ['4227', '102', '364', ' 108', ' 386', ' 123', '2'],
   ['4228', '102', '364', ' 108', ' 386', ' 122', '2'],
   ['4229', '102', '363', ' 108', ' 386', ' 122', '2'],
   ['4230', '102', '363', ' 107', ' 386', ' 123', '2'],
   ['4231', '102', '362', ' 108', ' 387', ' 124', '2'],
   ['4232', '102', '363', ' 108', ' 387', ' 125', '2'],
   ['4233', '102', '363', ' 108', ' 387', ' 125', '2'],
   ['4234', '102', '362', ' 108', ' 387', ' 125', '2'],
   ['4235', '102', '362', ' 109', ' 387', ' 125', '2'],
   ['4236', '102', '362', ' 109', ' 387', ' 126', '2'],
   ['4237', '102', '362', ' 109', ' 387', ' 126', '2'],
   ['4238', '102', '362', ' 109', ' 388', ' 126', '2'],
   ['4239', '102', '363', ' 109', ' 389', ' 127', '2'],
   ['4240', '102', '363', ' 109', ' 389', ' 127', '2'],
   ['4241', '102', '364', ' 110', ' 389', ' 128', '2'],
   ['4242', '102', '364', ' 110', ' 389', ' 128', '2'],
   ['4243', '102', '364', ' 110', ' 389', ' 128', '2'],
   ['4244', '102', '363', ' 110', ' 389', ' 129', '2'],
   ['4245', '102', '364', ' 110', ' 390', ' 129', '2'],
   ['4246', '102', '364', ' 111', ' 390', ' 130', '2'],
   ['4247', '102', '365', ' 112', ' 390', ' 130', '2'],
   ['4248', '102', '365', ' 113', ' 389', ' 131', '2'],
   ['4249', '102', '364', ' 114', ' 389', ' 131', '2'],
   ['4250', '102', '365', ' 115', ' 389', ' 132', '2'],
   ['4251', '102', '366', ' 116', ' 389', ' 132', '2'],
   ['4252', '102', '366', ' 116', ' 390', ' 133', '2'],
   ['4253', '102', '367', ' 117', ' 391', ' 133', '2'],
   ['4254', '102', '366', ' 116', ' 392', ' 134', '2'],
   ['4255', '102', '366', ' 117', ' 391', ' 134', '2'],
   ['4256', '102', '366', ' 117', ' 392', ' 135', '2'],
   ['4257', '102', '367', ' 118', ' 393', ' 135', '2'],
   ['4258', '102', '367', ' 117', ' 394', ' 135', '2'],
   ['4259', '102', '366', ' 117', ' 395', ' 137', '2'],
   ['4260', '102', '365', ' 117', ' 395', ' 138', '2'],
   ['4261', '102', '364', ' 116', ' 396', ' 139', '2'],
   ['4262', '102', '366', ' 117', ' 396', ' 139', '2'],
   ['4263', '102', '366', ' 117', ' 397', ' 140', '2'],
   ['4264', '102', '366', ' 116', ' 399', ' 141', '2'],
   ['4265', '102', '366', ' 117', ' 399', ' 142', '2'],
   ['4266', '102', '366', ' 118', ' 398', ' 142', '2'],
   ['4267', '102', '367', ' 118', ' 398', ' 142', '2'],
   ['4268', '102', '367', ' 119', ' 398', ' 143', '2'],
   ['4269', '102', '368', ' 120', ' 398', ' 144', '2'],
   ['4270', '102', '368', ' 121', ' 397', ' 144', '2'],
   ['4271', '102', '369', ' 123', ' 397', ' 145', '2'],
   ['4272', '102', '369', ' 124', ' 398', ' 146', '2'],
   ['4273', '102', '370', ' 125', ' 398', ' 147', '2'],
   ['4274', '102', '371', ' 125', ' 399', ' 147', '2'],
   ['4275', '102', '371', ' 126', ' 399', ' 148', '2'],
   ['4276', '102', '370', ' 127', ' 400', ' 149', '2'],
   ['4277', '102', '369', ' 127', ' 401', ' 150', '2'],
   ['4278', '102', '368', ' 126', ' 401', ' 151', '2'],
   ['4279', '102', '369', ' 127', ' 402', ' 151', '2'],
   ['4280', '102', '370', ' 129', ' 401', ' 152', '2'],
   ['4281', '102', '369', ' 129', ' 401', ' 153', '2'],
   ['4282', '102', '369', ' 129', ' 402', ' 154', '2'],
   ['4283', '102', '368', ' 129', ' 402', ' 155', '2'],
   ['4284', '102', '368', ' 129', ' 403', ' 156', '2'],
   ['4285', '102', '368', ' 130', ' 403', ' 157', '2'],
   ['4286', '102', '368', ' 131', ' 404', ' 158', '2'],
   ['4287', '102', '369', ' 133', ' 403', ' 159', '2'],
   ['4288', '102', '370', ' 134', ' 403', ' 160', '2'],
   ['4289', '102', '369', ' 135', ' 405', ' 162', '2'],
   ['4290', '102', '369', ' 136', ' 406', ' 164', '2'],
   ['4291', '102', '370', ' 137', ' 407', ' 166', '2'],
   ['4292', '102', '370', ' 139', ' 406', ' 167', '2'],
   ['4293', '102', '371', ' 139', ' 408', ' 168', '2'],
   ['4294', '102', '371', ' 140', ' 408', ' 169', '2'],
   ['4295', '102', '370', ' 140', ' 410', ' 171', '2'],
   ['4296', '102', '371', ' 141', ' 410', ' 172', '2'],
   ['4297', '102', '372', ' 143', ' 411', ' 173', '2'],
   ['4298', '102', '371', ' 142', ' 412', ' 174', '2'],
   ['4299', '102', '371', ' 143', ' 413', ' 177', '2'],
   ['4300', '102', '371', ' 144', ' 414', ' 178', '2'],
   ['4301', '102', '372', ' 147', ' 414', ' 180', '2'],
   ['4302', '102', '373', ' 148', ' 415', ' 181', '2'],
   ['4303', '102', '373', ' 149', ' 416', ' 184', '2'],
   ['4304', '102', '375', ' 152', ' 417', ' 186', '2'],
   ['4305', '102', '376', ' 153', ' 418', ' 187', '2'],
   ['4306', '102', '376', ' 155', ' 419', ' 189', '2'],
   ['4307', '102', '378', ' 156', ' 421', ' 191', '2'],
   ['4308', '102', '379', ' 157', ' 423', ' 193', '2'],
   ['4309', '102', '380', ' 158', ' 425', ' 194', '2'],
   ['4310', '102', '381', ' 159', ' 427', ' 197', '2'],
   ['4311', '102', '381', ' 161', ' 428', ' 200', '2'],
   ['4312', '102', '381', ' 163', ' 430', ' 203', '2'],
   ['4313', '102', '382', ' 165', ' 432', ' 205', '2'],
   ['4314', '102', '384', ' 167', ' 433', ' 207', '2'],
   ['4315', '102', '386', ' 168', ' 436', ' 209', '2'],
   ['4316', '102', '388', ' 169', ' 440', ' 212', '2'],
   ['4317', '102', '387', ' 171', ' 441', ' 216', '2'],
   ['4318', '102', '388', ' 173', ' 444', ' 220', '2'],
   ['4319', '102', '389', ' 175', ' 447', ' 223', '2'],
   ['4320', '102', '390', ' 176', ' 449', ' 226', '2'],
   ['4321', '102', '392', ' 178', ' 453', ' 229', '2'],
   ['4322', '102', '394', ' 180', ' 456', ' 232', '2'],
   ['4323', '102', '396', ' 183', ' 458', ' 235', '2'],
   ['4324', '102', '397', ' 185', ' 463', ' 241', '2'],
   ['4325', '102', '400', ' 189', ' 466', ' 246', '2'],
   ['4326', '102', '402', ' 193', ' 468', ' 249', '2'],
   ['4327', '102', '405', ' 196', ' 472', ' 253', '2'],
   ['4328', '102', '407', ' 199', ' 477', ' 258', '2'],
   ['4329', '102', '409', ' 200', ' 482', ' 262', '2'],
   ['4330', '102', '409', ' 203', ' 487', ' 269', '2'],
   ['4331', '102', '412', ' 207', ' 492', ' 274', '2'],
   ['4332', '102', '416', ' 211', ' 496', ' 279', '2'],
   ['4333', '102', '417', ' 214', ' 503', ' 287', '2'],
   ['4334', '102', '421', ' 219', ' 509', ' 294', '2'],
   ['4335', '102', '424', ' 222', ' 515', ' 300', '2'],
   ['4336', '102', '426', ' 226', ' 521', ' 307', '2'],
   ['4337', '102', '432', ' 231', ' 528', ' 314', '2'],
   ['4338', '102', '435', ' 236', ' 536', ' 322', '2'],
   ['4339', '102', '439', ' 242', ' 543', ' 330', '2'],
   ['4340', '102', '444', ' 248', ' 551', ' 340', '2'],
   ['4341', '102', '450', ' 254', ' 560', ' 349', '2'],
   ['4342', '102', '455', ' 261', ' 571', ' 360', '2'],
   ['4343', '102', '461', ' 267', ' 581', ' 371', '2'],
   ['4344', '102', '466', ' 274', ' 592', ' 383', '2'],
   ['4345', '102', '471', ' 281', ' 605', ' 398', '2'],
   ['4346', '102', '479', ' 290', ' 616', ' 409', '2'],
   ['4347', '102', '491', ' 298', ' 626', ' 415', '2'],
   ['4348', '102', '504', ' 307', ' 640', ' 421', '2'],
   ['4349', '102', '518', ' 317', ' 643', ' 419', '2'],
   ['4350', '102', '532', ' 328', ' 646', ' 417', '2']]},
 {'109': [['4420', '109', '350', ' 111', ' 373', ' 130', '2'],
   ['4424', '109', '348', ' 108', ' 377', ' 131', '2'],
   ['4425', '109', '349', ' 109', ' 377', ' 132', '2'],
   ['4426', '109', '350', ' 111', ' 377', ' 133', '2'],
   ['4427', '109', '351', ' 112', ' 377', ' 134', '2'],
   ['4428', '109', '351', ' 112', ' 377', ' 134', '2'],
   ['4429', '109', '351', ' 113', ' 377', ' 134', '2'],
   ['4430', '109', '351', ' 113', ' 377', ' 134', '2'],
   ['4431', '109', '351', ' 113', ' 377', ' 134', '2'],
   ['4432', '109', '353', ' 114', ' 377', ' 135', '2'],
   ['4433', '109', '352', ' 114', ' 378', ' 136', '2'],
   ['4434', '109', '352', ' 114', ' 379', ' 137', '2'],
   ['4435', '109', '352', ' 113', ' 380', ' 137', '2'],
   ['4436', '109', '352', ' 113', ' 381', ' 138', '2'],
   ['4437', '109', '352', ' 113', ' 381', ' 138', '2'],
   ['4438', '109', '351', ' 112', ' 382', ' 138', '2'],
   ['4439', '109', '352', ' 112', ' 382', ' 139', '2'],
   ['4440', '109', '352', ' 113', ' 382', ' 139', '2'],
   ['4441', '109', '353', ' 114', ' 382', ' 140', '2'],
   ['4442', '109', '354', ' 114', ' 383', ' 140', '2'],
   ['4443', '109', '355', ' 115', ' 383', ' 140', '2'],
   ['4444', '109', '354', ' 115', ' 384', ' 140', '2'],
   ['4445', '109', '354', ' 115', ' 384', ' 141', '2'],
   ['4446', '109', '355', ' 115', ' 384', ' 141', '2'],
   ['4447', '109', '356', ' 116', ' 383', ' 141', '2'],
   ['4448', '109', '356', ' 116', ' 384', ' 141', '2'],
   ['4449', '109', '356', ' 117', ' 384', ' 141', '2'],
   ['4450', '109', '356', ' 117', ' 385', ' 142', '2'],
   ['4451', '109', '356', ' 117', ' 385', ' 143', '2'],
   ['4452', '109', '357', ' 117', ' 385', ' 143', '2'],
   ['4453', '109', '357', ' 118', ' 385', ' 143', '2'],
   ['4454', '109', '357', ' 118', ' 386', ' 144', '2'],
   ['4455', '109', '358', ' 119', ' 385', ' 144', '2'],
   ['4456', '109', '358', ' 119', ' 386', ' 144', '2'],
   ['4457', '109', '357', ' 119', ' 386', ' 145', '2'],
   ['4458', '109', '358', ' 120', ' 386', ' 145', '2'],
   ['4459', '109', '359', ' 121', ' 386', ' 146', '2'],
   ['4460', '109', '359', ' 122', ' 387', ' 146', '2'],
   ['4461', '109', '359', ' 122', ' 387', ' 147', '2'],
   ['4462', '109', '359', ' 122', ' 387', ' 147', '2'],
   ['4463', '109', '360', ' 122', ' 388', ' 147', '2'],
   ['4464', '109', '361', ' 123', ' 388', ' 147', '2'],
   ['4465', '109', '361', ' 124', ' 389', ' 147', '2'],
   ['4466', '109', '361', ' 124', ' 390', ' 149', '2'],
   ['4467', '109', '361', ' 125', ' 391', ' 150', '2'],
   ['4468', '109', '361', ' 125', ' 391', ' 151', '2'],
   ['4469', '109', '360', ' 126', ' 392', ' 151', '2'],
   ['4470', '109', '361', ' 126', ' 392', ' 152', '2'],
   ['4471', '109', '362', ' 127', ' 393', ' 152', '2'],
   ['4472', '109', '362', ' 127', ' 394', ' 152', '2'],
   ['4473', '109', '363', ' 127', ' 394', ' 153', '2'],
   ['4474', '109', '363', ' 128', ' 395', ' 153', '2'],
   ['4475', '109', '363', ' 128', ' 395', ' 154', '2'],
   ['4476', '109', '364', ' 128', ' 396', ' 154', '2'],
   ['4477', '109', '364', ' 128', ' 396', ' 155', '2'],
   ['4478', '109', '364', ' 129', ' 397', ' 156', '2'],
   ['4479', '109', '364', ' 129', ' 397', ' 156', '2'],
   ['4480', '109', '365', ' 129', ' 399', ' 157', '2'],
   ['4481', '109', '365', ' 129', ' 400', ' 158', '2'],
   ['4482', '109', '365', ' 129', ' 400', ' 158', '2'],
   ['4483', '109', '364', ' 129', ' 400', ' 158', '2'],
   ['4484', '109', '365', ' 129', ' 401', ' 159', '2'],
   ['4485', '109', '365', ' 130', ' 402', ' 160', '2'],
   ['4486', '109', '364', ' 130', ' 402', ' 161', '2'],
   ['4487', '109', '365', ' 130', ' 403', ' 163', '2'],
   ['4488', '109', '366', ' 131', ' 404', ' 164', '2'],
   ['4489', '109', '367', ' 132', ' 405', ' 164', '2'],
   ['4490', '109', '367', ' 131', ' 406', ' 165', '2'],
   ['4491', '109', '367', ' 131', ' 406', ' 165', '2'],
   ['4492', '109', '368', ' 132', ' 406', ' 166', '2'],
   ['4493', '109', '369', ' 133', ' 407', ' 167', '2'],
   ['4494', '109', '369', ' 134', ' 408', ' 168', '2'],
   ['4495', '109', '369', ' 135', ' 408', ' 169', '2'],
   ['4496', '109', '370', ' 135', ' 409', ' 170', '2'],
   ['4497', '109', '370', ' 136', ' 410', ' 171', '2'],
   ['4498', '109', '370', ' 136', ' 410', ' 171', '2'],
   ['4499', '109', '371', ' 136', ' 411', ' 171', '2'],
   ['4500', '109', '371', ' 138', ' 411', ' 173', '2'],
   ['4501', '109', '371', ' 139', ' 411', ' 174', '2'],
   ['4502', '109', '372', ' 140', ' 412', ' 175', '2'],
   ['4503', '109', '373', ' 140', ' 414', ' 176', '2'],
   ['4504', '109', '374', ' 140', ' 415', ' 177', '2'],
   ['4505', '109', '374', ' 141', ' 416', ' 178', '2'],
   ['4506', '109', '374', ' 142', ' 416', ' 179', '2'],
   ['4507', '109', '375', ' 142', ' 416', ' 180', '2'],
   ['4508', '109', '375', ' 144', ' 417', ' 181', '2'],
   ['4509', '109', '376', ' 145', ' 418', ' 182', '2'],
   ['4510', '109', '376', ' 145', ' 419', ' 183', '2'],
   ['4511', '109', '377', ' 147', ' 419', ' 185', '2'],
   ['4512', '109', '378', ' 147', ' 421', ' 186', '2'],
   ['4513', '109', '378', ' 147', ' 422', ' 187', '2'],
   ['4514', '109', '379', ' 148', ' 423', ' 188', '2'],
   ['4515', '109', '379', ' 149', ' 423', ' 189', '2'],
   ['4516', '109', '380', ' 150', ' 424', ' 189', '2'],
   ['4517', '109', '381', ' 150', ' 425', ' 190', '2'],
   ['4518', '109', '381', ' 151', ' 427', ' 193', '2'],
   ['4519', '109', '381', ' 151', ' 429', ' 194', '2'],
   ['4520', '109', '381', ' 151', ' 431', ' 197', '2'],
   ['4521', '109', '382', ' 154', ' 431', ' 199', '2'],
   ['4522', '109', '383', ' 154', ' 433', ' 201', '2'],
   ['4523', '109', '385', ' 156', ' 434', ' 202', '2'],
   ['4524', '109', '385', ' 157', ' 435', ' 204', '2'],
   ['4525', '109', '385', ' 157', ' 436', ' 205', '2'],
   ['4526', '109', '386', ' 158', ' 437', ' 207', '2'],
   ['4527', '109', '388', ' 160', ' 439', ' 208', '2'],
   ['4528', '109', '390', ' 162', ' 441', ' 209', '2'],
   ['4529', '109', '390', ' 162', ' 442', ' 211', '2'],
   ['4530', '109', '390', ' 163', ' 444', ' 213', '2'],
   ['4531', '109', '389', ' 162', ' 446', ' 215', '2'],
   ['4532', '109', '389', ' 163', ' 447', ' 216', '2'],
   ['4533', '109', '390', ' 165', ' 448', ' 219', '2'],
   ['4534', '109', '391', ' 168', ' 450', ' 223', '2'],
   ['4535', '109', '392', ' 169', ' 452', ' 225', '2'],
   ['4536', '109', '393', ' 171', ' 454', ' 227', '2'],
   ['4537', '109', '394', ' 173', ' 454', ' 228', '2'],
   ['4538', '109', '396', ' 174', ' 456', ' 230', '2'],
   ['4539', '109', '396', ' 175', ' 458', ' 233', '2'],
   ['4540', '109', '398', ' 176', ' 459', ' 233', '2'],
   ['4541', '109', '400', ' 179', ' 462', ' 236', '2'],
   ['4542', '109', '401', ' 182', ' 465', ' 240', '2'],
   ['4543', '109', '401', ' 183', ' 467', ' 243', '2'],
   ['4544', '109', '401', ' 184', ' 471', ' 248', '2'],
   ['4545', '109', '403', ' 186', ' 474', ' 251', '2'],
   ['4546', '109', '405', ' 188', ' 477', ' 254', '2'],
   ['4547', '109', '408', ' 192', ' 477', ' 255', '2'],
   ['4548', '109', '408', ' 193', ' 481', ' 260', '2'],
   ['4549', '109', '410', ' 195', ' 484', ' 262', '2'],
   ['4550', '109', '411', ' 196', ' 488', ' 265', '2'],
   ['4551', '109', '414', ' 200', ' 491', ' 269', '2'],
   ['4552', '109', '415', ' 201', ' 495', ' 274', '2'],
   ['4553', '109', '416', ' 203', ' 499', ' 278', '2'],
   ['4554', '109', '417', ' 205', ' 503', ' 282', '2'],
   ['4555', '109', '418', ' 208', ' 505', ' 286', '2'],
   ['4556', '109', '419', ' 209', ' 510', ' 292', '2'],
   ['4557', '109', '421', ' 212', ' 513', ' 296', '2'],
   ['4558', '109', '423', ' 214', ' 517', ' 299', '2'],
   ['4559', '109', '426', ' 217', ' 521', ' 303', '2'],
   ['4560', '109', '427', ' 219', ' 527', ' 310', '2'],
   ['4561', '109', '430', ' 223', ' 532', ' 316', '2'],
   ['4562', '109', '432', ' 226', ' 536', ' 322', '2'],
   ['4563', '109', '435', ' 230', ' 541', ' 328', '2'],
   ['4564', '109', '436', ' 232', ' 547', ' 334', '2'],
   ['4565', '109', '440', ' 236', ' 551', ' 339', '2'],
   ['4566', '109', '442', ' 241', ' 557', ' 347', '2'],
   ['4567', '109', '446', ' 244', ' 564', ' 354', '2'],
   ['4569', '109', '452', ' 252', ' 575', ' 366', '2'],
   ['4570', '109', '455', ' 258', ' 583', ' 376', '2'],
   ['4571', '109', '460', ' 263', ' 591', ' 384', '2'],
   ['4572', '109', '461', ' 268', ' 602', ' 400', '2'],
   ['4573', '109', '466', ' 274', ' 610', ' 408', '2'],
   ['4574', '109', '473', ' 278', ' 617', ' 413', '2'],
   ['4575', '109', '481', ' 284', ' 621', ' 414', '2'],
   ['4576', '109', '489', ' 291', ' 626', ' 415', '2'],
   ['4577', '109', '500', ' 298', ' 634', ' 416', '2'],
   ['4578', '109', '507', ' 303', ' 636', ' 414', '2'],
   ['4579', '109', '514', ' 310', ' 637', ' 412', '2'],
   ['4580', '109', '523', ' 318', ' 643', ' 413', '2'],
   ['4581', '109', '532', ' 325', ' 648', ' 413', '2'],
   ['4582', '109', '542', ' 332', ' 653', ' 412', '2'],
   ['4583', '109', '556', ' 342', ' 656', ' 410', '2'],
   ['4584', '109', '563', ' 350', ' 658', ' 411', '2'],
   ['4585', '109', '574', ' 360', ' 661', ' 412', '2']]},
 {'117': [['4811', '117', '342', ' 117', ' 367', ' 134', '2'],
   ['4812', '117', '341', ' 118', ' 368', ' 135', '2'],
   ['4813', '117', '340', ' 118', ' 368', ' 136', '2'],
   ['4815', '117', '341', ' 122', ' 366', ' 138', '2'],
   ['4821', '117', '341', ' 127', ' 367', ' 143', '2'],
   ['4822', '117', '341', ' 127', ' 368', ' 144', '2'],
   ['4823', '117', '341', ' 128', ' 367', ' 145', '2'],
   ['4825', '117', '340', ' 129', ' 367', ' 147', '2'],
   ['4826', '117', '339', ' 129', ' 368', ' 147', '2'],
   ['4827', '117', '338', ' 129', ' 369', ' 149', '2'],
   ['4828', '117', '338', ' 129', ' 370', ' 150', '2'],
   ['4829', '117', '338', ' 129', ' 371', ' 151', '2'],
   ['4830', '117', '338', ' 130', ' 371', ' 152', '2'],
   ['4831', '117', '339', ' 132', ' 372', ' 153', '2'],
   ['4832', '117', '340', ' 134', ' 370', ' 154', '2'],
   ['4833', '117', '340', ' 135', ' 371', ' 155', '2'],
   ['4834', '117', '338', ' 135', ' 372', ' 156', '2'],
   ['4835', '117', '338', ' 135', ' 373', ' 157', '2'],
   ['4836', '117', '336', ' 135', ' 373', ' 158', '2'],
   ['4837', '117', '336', ' 137', ' 372', ' 159', '2'],
   ['4838', '117', '337', ' 137', ' 373', ' 160', '2'],
   ['4839', '117', '338', ' 141', ' 372', ' 162', '2'],
   ['4840', '117', '336', ' 140', ' 374', ' 164', '2'],
   ['4841', '117', '336', ' 140', ' 374', ' 165', '2'],
   ['4842', '117', '336', ' 141', ' 375', ' 166', '2'],
   ['4843', '117', '335', ' 140', ' 377', ' 168', '2'],
   ['4844', '117', '334', ' 141', ' 377', ' 169', '2'],
   ['4845', '117', '334', ' 142', ' 377', ' 171', '2'],
   ['4846', '117', '333', ' 143', ' 378', ' 173', '2'],
   ['4847', '117', '333', ' 144', ' 376', ' 174', '2'],
   ['4848', '117', '333', ' 144', ' 379', ' 177', '2'],
   ['4849', '117', '333', ' 145', ' 380', ' 178', '2'],
   ['4850', '117', '332', ' 146', ' 379', ' 180', '2'],
   ['4851', '117', '332', ' 147', ' 380', ' 182', '2'],
   ['4852', '117', '332', ' 149', ' 379', ' 184', '2'],
   ['4853', '117', '331', ' 149', ' 379', ' 185', '2'],
   ['4854', '117', '332', ' 150', ' 380', ' 186', '2'],
   ['4855', '117', '331', ' 152', ' 380', ' 189', '2'],
   ['4856', '117', '333', ' 154', ' 380', ' 191', '2'],
   ['4857', '117', '333', ' 155', ' 381', ' 193', '2'],
   ['4858', '117', '332', ' 157', ' 381', ' 196', '2'],
   ['4859', '117', '332', ' 159', ' 381', ' 199', '2'],
   ['4860', '117', '332', ' 161', ' 382', ' 201', '2'],
   ['4861', '117', '332', ' 163', ' 383', ' 204', '2'],
   ['4862', '117', '333', ' 166', ' 382', ' 206', '2'],
   ['4863', '117', '333', ' 168', ' 383', ' 209', '2'],
   ['4864', '117', '334', ' 169', ' 384', ' 211', '2'],
   ['4865', '117', '333', ' 171', ' 385', ' 214', '2'],
   ['4866', '117', '332', ' 173', ' 385', ' 218', '2'],
   ['4867', '117', '331', ' 175', ' 387', ' 222', '2'],
   ['4868', '117', '331', ' 176', ' 388', ' 225', '2'],
   ['4869', '117', '330', ' 177', ' 390', ' 228', '2'],
   ['4870', '117', '331', ' 181', ' 391', ' 232', '2'],
   ['4871', '117', '333', ' 184', ' 393', ' 236', '2'],
   ['4872', '117', '334', ' 189', ' 393', ' 240', '2'],
   ['4873', '117', '331', ' 190', ' 395', ' 246', '2'],
   ['4874', '117', '330', ' 193', ' 395', ' 249', '2'],
   ['4875', '117', '331', ' 196', ' 398', ' 255', '2'],
   ['4876', '117', '330', ' 199', ' 401', ' 261', '2'],
   ['4877', '117', '330', ' 203', ' 401', ' 266', '2'],
   ['4878', '117', '330', ' 208', ' 404', ' 274', '2'],
   ['4879', '117', '329', ' 211', ' 405', ' 279', '2'],
   ['4880', '117', '330', ' 215', ' 408', ' 284', '2'],
   ['4881', '117', '328', ' 219', ' 410', ' 291', '2'],
   ['4882', '117', '329', ' 223', ' 413', ' 298', '2'],
   ['4883', '117', '329', ' 227', ' 416', ' 306', '2'],
   ['4884', '117', '330', ' 234', ' 420', ' 315', '2'],
   ['4885', '117', '331', ' 240', ' 423', ' 323', '2'],
   ['4886', '117', '332', ' 245', ' 427', ' 332', '2'],
   ['4887', '117', '332', ' 252', ' 431', ' 343', '2'],
   ['4888', '117', '332', ' 258', ' 435', ' 353', '2'],
   ['4889', '117', '333', ' 266', ' 440', ' 365', '2'],
   ['4890', '117', '330', ' 273', ' 445', ' 379', '2'],
   ['4891', '117', '328', ' 280', ' 451', ' 394', '2'],
   ['4892', '117', '327', ' 288', ' 455', ' 406', '2'],
   ['4893', '117', '331', ' 299', ' 457', ' 414', '2'],
   ['4894', '117', '339', ' 309', ' 459', ' 417', '2'],
   ['4895', '117', '348', ' 320', ' 451', ' 409', '2'],
   ['4896', '117', '355', ' 332', ' 452', ' 412', '2'],
   ['4897', '117', '363', ' 346', ' 450', ' 413', '2'],
   ['4898', '117', '370', ' 362', ' 443', ' 413', '2']]},
 {'122': [['4848', '122', '357', ' 117', ' 383', ' 137', '2'],
   ['4849', '122', '357', ' 118', ' 383', ' 138', '2'],
   ['4850', '122', '356', ' 117', ' 384', ' 139', '2'],
   ['4853', '122', '356', ' 117', ' 384', ' 139', '2'],
   ['4858', '122', '356', ' 125', ' 382', ' 145', '2'],
   ['4861', '122', '357', ' 127', ' 383', ' 147', '2'],
   ['4862', '122', '357', ' 128', ' 383', ' 147', '2'],
   ['4863', '122', '357', ' 128', ' 384', ' 148', '2'],
   ['4864', '122', '356', ' 128', ' 386', ' 150', '2'],
   ['4865', '122', '355', ' 128', ' 387', ' 151', '2'],
   ['4866', '122', '355', ' 129', ' 388', ' 152', '2'],
   ['4867', '122', '355', ' 129', ' 388', ' 153', '2'],
   ['4868', '122', '356', ' 130', ' 387', ' 153', '2'],
   ['4869', '122', '356', ' 131', ' 387', ' 154', '2'],
   ['4870', '122', '355', ' 130', ' 388', ' 155', '2'],
   ['4871', '122', '355', ' 131', ' 388', ' 156', '2'],
   ['4872', '122', '354', ' 132', ' 388', ' 157', '2'],
   ['4873', '122', '354', ' 132', ' 389', ' 158', '2'],
   ['4874', '122', '355', ' 133', ' 389', ' 159', '2'],
   ['4875', '122', '355', ' 134', ' 388', ' 160', '2'],
   ['4876', '122', '355', ' 135', ' 389', ' 162', '2'],
   ['4877', '122', '355', ' 135', ' 391', ' 162', '2'],
   ['4878', '122', '355', ' 136', ' 392', ' 164', '2'],
   ['4879', '122', '354', ' 136', ' 393', ' 166', '2'],
   ['4880', '122', '355', ' 138', ' 394', ' 167', '2'],
   ['4881', '122', '353', ' 138', ' 393', ' 168', '2'],
   ['4882', '122', '354', ' 139', ' 392', ' 169', '2'],
   ['4883', '122', '355', ' 141', ' 395', ' 171', '2'],
   ['4884', '122', '354', ' 141', ' 394', ' 172', '2'],
   ['4885', '122', '353', ' 142', ' 394', ' 173', '2'],
   ['4886', '122', '354', ' 144', ' 394', ' 174', '2'],
   ['4887', '122', '354', ' 145', ' 393', ' 175', '2'],
   ['4888', '122', '354', ' 147', ' 395', ' 178', '2'],
   ['4889', '122', '354', ' 148', ' 395', ' 179', '2'],
   ['4890', '122', '354', ' 149', ' 395', ' 180', '2'],
   ['4891', '122', '353', ' 150', ' 395', ' 182', '2'],
   ['4892', '122', '353', ' 151', ' 396', ' 184', '2'],
   ['4893', '122', '353', ' 152', ' 397', ' 185', '2'],
   ['4894', '122', '353', ' 153', ' 397', ' 186', '2'],
   ['4895', '122', '353', ' 153', ' 398', ' 188', '2'],
   ['4896', '122', '353', ' 155', ' 399', ' 190', '2'],
   ['4897', '122', '354', ' 156', ' 399', ' 191', '2'],
   ['4898', '122', '353', ' 158', ' 400', ' 194', '2'],
   ['4899', '122', '353', ' 159', ' 401', ' 196', '2'],
   ['4900', '122', '354', ' 160', ' 402', ' 199', '2'],
   ['4901', '122', '354', ' 161', ' 403', ' 200', '2'],
   ['4902', '122', '353', ' 162', ' 403', ' 202', '2'],
   ['4903', '122', '353', ' 162', ' 403', ' 204', '2'],
   ['4904', '122', '353', ' 165', ' 403', ' 207', '2'],
   ['4905', '122', '353', ' 166', ' 404', ' 209', '2'],
   ['4906', '122', '354', ' 168', ' 406', ' 211', '2'],
   ['4907', '122', '353', ' 170', ' 406', ' 214', '2'],
   ['4908', '122', '354', ' 173', ' 406', ' 217', '2'],
   ['4909', '122', '353', ' 174', ' 407', ' 220', '2'],
   ['4910', '122', '354', ' 176', ' 407', ' 223', '2'],
   ['4911', '122', '355', ' 178', ' 410', ' 226', '2'],
   ['4912', '122', '354', ' 179', ' 410', ' 228', '2'],
   ['4913', '122', '354', ' 181', ' 412', ' 232', '2'],
   ['4914', '122', '353', ' 182', ' 413', ' 236', '2'],
   ['4915', '122', '353', ' 185', ' 414', ' 239', '2'],
   ['4916', '122', '354', ' 188', ' 416', ' 243', '2'],
   ['4917', '122', '355', ' 191', ' 419', ' 247', '2'],
   ['4918', '122', '355', ' 194', ' 419', ' 252', '2'],
   ['4919', '122', '354', ' 195', ' 421', ' 256', '2'],
   ['4920', '122', '354', ' 199', ' 423', ' 260', '2'],
   ['4921', '122', '354', ' 202', ' 424', ' 265', '2'],
   ['4922', '122', '353', ' 204', ' 426', ' 271', '2'],
   ['4923', '122', '355', ' 208', ' 428', ' 274', '2'],
   ['4924', '122', '356', ' 212', ' 430', ' 279', '2'],
   ['4925', '122', '357', ' 216', ' 433', ' 284', '2'],
   ['4926', '122', '356', ' 219', ' 436', ' 292', '2'],
   ['4927', '122', '356', ' 222', ' 439', ' 298', '2'],
   ['4928', '122', '356', ' 227', ' 441', ' 305', '2'],
   ['4929', '122', '357', ' 231', ' 444', ' 311', '2'],
   ['4930', '122', '357', ' 237', ' 446', ' 318', '2'],
   ['4931', '122', '358', ' 241', ' 449', ' 325', '2'],
   ['4932', '122', '358', ' 247', ' 452', ' 334', '2'],
   ['4933', '122', '357', ' 252', ' 455', ' 343', '2'],
   ['4934', '122', '358', ' 258', ' 460', ' 351', '2'],
   ['4935', '122', '359', ' 265', ' 464', ' 361', '2'],
   ['4936', '122', '358', ' 271', ' 468', ' 372', '2'],
   ['4937', '122', '357', ' 278', ' 474', ' 386', '2'],
   ['4938', '122', '356', ' 286', ' 480', ' 400', '2'],
   ['4939', '122', '359', ' 293', ' 485', ' 409', '2'],
   ['4940', '122', '363', ' 301', ' 488', ' 415', '2'],
   ['4941', '122', '368', ' 310', ' 489', ' 419', '2'],
   ['4942', '122', '379', ' 319', ' 481', ' 407', '2']]},
 {'136': [['5412', '136', '379', ' 105', ' 396', ' 118', '2'],
   ['5415', '136', '380', ' 105', ' 396', ' 119', '2'],
   ['5420', '136', '380', ' 106', ' 397', ' 119', '2'],
   ['5422', '136', '380', ' 106', ' 397', ' 120', '2'],
   ['5423', '136', '380', ' 106', ' 398', ' 121', '2'],
   ['5425', '136', '381', ' 107', ' 398', ' 121', '2'],
   ['5427', '136', '382', ' 107', ' 398', ' 121', '2'],
   ['5429', '136', '382', ' 108', ' 399', ' 121', '2'],
   ['5430', '136', '382', ' 108', ' 399', ' 122', '2'],
   ['5431', '136', '382', ' 108', ' 399', ' 122', '2'],
   ['5441', '136', '383', ' 108', ' 404', ' 124', '2'],
   ['5443', '136', '385', ' 109', ' 406', ' 126', '2'],
   ['5444', '136', '386', ' 110', ' 407', ' 127', '2'],
   ['5445', '136', '386', ' 111', ' 407', ' 127', '2'],
   ['5446', '136', '386', ' 111', ' 406', ' 127', '2'],
   ['5447', '136', '386', ' 111', ' 406', ' 127', '2'],
   ['5448', '136', '386', ' 111', ' 407', ' 127', '2'],
   ['5449', '136', '386', ' 112', ' 407', ' 128', '2'],
   ['5450', '136', '386', ' 112', ' 408', ' 129', '2'],
   ['5451', '136', '386', ' 112', ' 408', ' 129', '2'],
   ['5452', '136', '386', ' 112', ' 409', ' 130', '2'],
   ['5453', '136', '386', ' 111', ' 409', ' 130', '2'],
   ['5454', '136', '386', ' 112', ' 409', ' 130', '2'],
   ['5455', '136', '386', ' 112', ' 409', ' 131', '2'],
   ['5456', '136', '386', ' 112', ' 410', ' 131', '2'],
   ['5457', '136', '387', ' 112', ' 410', ' 132', '2'],
   ['5458', '136', '387', ' 113', ' 410', ' 132', '2'],
   ['5459', '136', '387', ' 113', ' 410', ' 132', '2'],
   ['5460', '136', '388', ' 114', ' 411', ' 133', '2'],
   ['5461', '136', '388', ' 114', ' 411', ' 134', '2'],
   ['5462', '136', '388', ' 115', ' 411', ' 134', '2'],
   ['5463', '136', '389', ' 116', ' 411', ' 135', '2'],
   ['5464', '136', '389', ' 116', ' 412', ' 135', '2'],
   ['5465', '136', '389', ' 116', ' 412', ' 135', '2'],
   ['5466', '136', '390', ' 116', ' 412', ' 135', '2'],
   ['5467', '136', '391', ' 117', ' 412', ' 134', '2'],
   ['5468', '136', '391', ' 117', ' 412', ' 134', '2'],
   ['5469', '136', '390', ' 117', ' 413', ' 136', '2'],
   ['5470', '136', '391', ' 117', ' 414', ' 137', '2'],
   ['5471', '136', '392', ' 118', ' 415', ' 138', '2'],
   ['5472', '136', '392', ' 118', ' 416', ' 138', '2'],
   ['5473', '136', '393', ' 118', ' 417', ' 139', '2'],
   ['5474', '136', '393', ' 118', ' 419', ' 139', '2'],
   ['5475', '136', '394', ' 118', ' 420', ' 140', '2'],
   ['5476', '136', '394', ' 118', ' 420', ' 140', '2'],
   ['5477', '136', '394', ' 117', ' 421', ' 141', '2'],
   ['5478', '136', '394', ' 117', ' 421', ' 141', '2'],
   ['5479', '136', '396', ' 119', ' 421', ' 142', '2'],
   ['5480', '136', '396', ' 120', ' 422', ' 142', '2'],
   ['5481', '136', '397', ' 120', ' 422', ' 143', '2'],
   ['5482', '136', '396', ' 121', ' 422', ' 143', '2'],
   ['5483', '136', '396', ' 121', ' 422', ' 144', '2'],
   ['5484', '136', '396', ' 122', ' 422', ' 145', '2'],
   ['5485', '136', '397', ' 123', ' 423', ' 145', '2'],
   ['5486', '136', '398', ' 124', ' 423', ' 146', '2'],
   ['5487', '136', '398', ' 125', ' 423', ' 147', '2'],
   ['5488', '136', '399', ' 125', ' 424', ' 147', '2'],
   ['5489', '136', '400', ' 125', ' 425', ' 147', '2'],
   ['5490', '136', '400', ' 126', ' 426', ' 147', '2'],
   ['5491', '136', '401', ' 126', ' 427', ' 148', '2'],
   ['5492', '136', '401', ' 127', ' 429', ' 150', '2'],
   ['5493', '136', '400', ' 126', ' 430', ' 151', '2'],
   ['5494', '136', '400', ' 127', ' 431', ' 152', '2'],
   ['5495', '136', '400', ' 126', ' 433', ' 152', '2'],
   ['5496', '136', '401', ' 126', ' 434', ' 153', '2'],
   ['5497', '136', '402', ' 126', ' 435', ' 154', '2'],
   ['5498', '136', '402', ' 127', ' 435', ' 154', '2'],
   ['5499', '136', '403', ' 127', ' 436', ' 155', '2'],
   ['5500', '136', '404', ' 128', ' 437', ' 155', '2'],
   ['5501', '136', '405', ' 129', ' 438', ' 156', '2'],
   ['5502', '136', '406', ' 130', ' 438', ' 157', '2'],
   ['5503', '136', '405', ' 130', ' 440', ' 158', '2'],
   ['5504', '136', '406', ' 129', ' 440', ' 158', '2'],
   ['5505', '136', '406', ' 129', ' 441', ' 159', '2'],
   ['5506', '136', '408', ' 130', ' 442', ' 159', '2'],
   ['5507', '136', '408', ' 131', ' 443', ' 161', '2'],
   ['5508', '136', '410', ' 133', ' 444', ' 162', '2'],
   ['5509', '136', '411', ' 133', ' 446', ' 163', '2'],
   ['5510', '136', '412', ' 134', ' 447', ' 164', '2'],
   ['5511', '136', '413', ' 135', ' 448', ' 164', '2'],
   ['5512', '136', '414', ' 135', ' 449', ' 165', '2'],
   ['5513', '136', '414', ' 136', ' 450', ' 166', '2'],
   ['5514', '136', '415', ' 137', ' 451', ' 167', '2'],
   ['5515', '136', '415', ' 137', ' 452', ' 168', '2'],
   ['5516', '136', '416', ' 138', ' 452', ' 169', '2'],
   ['5517', '136', '416', ' 139', ' 454', ' 171', '2'],
   ['5518', '136', '418', ' 140', ' 455', ' 172', '2'],
   ['5519', '136', '418', ' 141', ' 456', ' 174', '2'],
   ['5520', '136', '419', ' 141', ' 457', ' 175', '2'],
   ['5521', '136', '420', ' 142', ' 458', ' 176', '2'],
   ['5522', '136', '422', ' 143', ' 461', ' 178', '2'],
   ['5523', '136', '422', ' 144', ' 461', ' 179', '2'],
   ['5524', '136', '423', ' 145', ' 463', ' 180', '2'],
   ['5525', '136', '424', ' 145', ' 463', ' 181', '2'],
   ['5526', '136', '425', ' 147', ' 464', ' 181', '2'],
   ['5527', '136', '427', ' 148', ' 465', ' 183', '2'],
   ['5528', '136', '428', ' 147', ' 468', ' 184', '2'],
   ['5529', '136', '429', ' 149', ' 469', ' 185', '2'],
   ['5530', '136', '431', ' 150', ' 471', ' 186', '2'],
   ['5531', '136', '432', ' 152', ' 472', ' 188', '2'],
   ['5532', '136', '434', ' 152', ' 475', ' 189', '2'],
   ['5533', '136', '434', ' 153', ' 476', ' 191', '2'],
   ['5534', '136', '435', ' 154', ' 477', ' 193', '2'],
   ['5535', '136', '436', ' 155', ' 479', ' 194', '2'],
   ['5536', '136', '437', ' 156', ' 481', ' 196', '2'],
   ['5537', '136', '439', ' 157', ' 483', ' 198', '2'],
   ['5538', '136', '441', ' 158', ' 485', ' 199', '2'],
   ['5539', '136', '441', ' 159', ' 487', ' 202', '2'],
   ['5540', '136', '442', ' 160', ' 489', ' 204', '2'],
   ['5541', '136', '443', ' 161', ' 490', ' 205', '2'],
   ['5542', '136', '445', ' 163', ' 493', ' 206', '2'],
   ['5543', '136', '446', ' 163', ' 495', ' 208', '2'],
   ['5544', '136', '448', ' 166', ' 497', ' 210', '2'],
   ['5545', '136', '449', ' 167', ' 499', ' 212', '2'],
   ['5546', '136', '450', ' 168', ' 501', ' 214', '2'],
   ['5548', '136', '451', ' 169', ' 505', ' 219', '2'],
   ['5549', '136', '453', ' 170', ' 508', ' 221', '2'],
   ['5550', '136', '456', ' 174', ' 510', ' 224', '2'],
   ['5551', '136', '458', ' 176', ' 513', ' 226', '2'],
   ['5552', '136', '458', ' 176', ' 516', ' 229', '2'],
   ['5553', '136', '461', ' 177', ' 518', ' 231', '2'],
   ['5554', '136', '463', ' 179', ' 520', ' 233', '2'],
   ['5555', '136', '464', ' 180', ' 524', ' 235', '2'],
   ['5556', '136', '466', ' 181', ' 527', ' 239', '2'],
   ['5557', '136', '468', ' 183', ' 531', ' 243', '2'],
   ['5558', '136', '470', ' 185', ' 534', ' 245', '2'],
   ['5559', '136', '473', ' 188', ' 537', ' 248', '2'],
   ['5560', '136', '477', ' 193', ' 539', ' 251', '2'],
   ['5561', '136', '477', ' 192', ' 543', ' 255', '2'],
   ['5562', '136', '480', ' 194', ' 547', ' 257', '2'],
   ['5563', '136', '482', ' 196', ' 551', ' 260', '2'],
   ['5564', '136', '484', ' 197', ' 555', ' 262', '2'],
   ['5565', '136', '486', ' 199', ' 559', ' 267', '2'],
   ['5566', '136', '488', ' 201', ' 563', ' 272', '2'],
   ['5567', '136', '491', ' 202', ' 568', ' 274', '2'],
   ['5568', '136', '494', ' 205', ' 571', ' 278', '2'],
   ['5569', '136', '497', ' 208', ' 575', ' 282', '2'],
   ['5570', '136', '501', ' 212', ' 579', ' 285', '2'],
   ['5571', '136', '504', ' 215', ' 584', ' 290', '2'],
   ['5572', '136', '508', ' 218', ' 589', ' 296', '2'],
   ['5573', '136', '512', ' 221', ' 596', ' 300', '2'],
   ['5574', '136', '516', ' 223', ' 604', ' 306', '2'],
   ['5575', '136', '520', ' 226', ' 610', ' 311', '2'],
   ['5576', '136', '522', ' 229', ' 614', ' 316', '2'],
   ['5577', '136', '526', ' 232', ' 621', ' 323', '2'],
   ['5578', '136', '531', ' 236', ' 628', ' 329', '2'],
   ['5579', '136', '535', ' 241', ' 634', ' 335', '2'],
   ['5580', '136', '540', ' 245', ' 641', ' 341', '2'],
   ['5581', '136', '545', ' 248', ' 649', ' 347', '2'],
   ['5582', '136', '549', ' 252', ' 657', ' 354', '2'],
   ['5583', '136', '554', ' 256', ' 665', ' 362', '2'],
   ['5584', '136', '560', ' 261', ' 674', ' 369', '2'],
   ['5585', '136', '565', ' 266', ' 683', ' 378', '2'],
   ['5586', '136', '571', ' 270', ' 693', ' 386', '2'],
   ['5587', '136', '577', ' 275', ' 704', ' 397', '2'],
   ['5588', '136', '582', ' 280', ' 714', ' 406', '2'],
   ['5589', '136', '591', ' 285', ' 724', ' 412', '2'],
   ['5590', '136', '601', ' 292', ' 732', ' 416', '2'],
   ['5591', '136', '615', ' 298', ' 743', ' 416', '2'],
   ['5592', '136', '624', ' 305', ' 750', ' 417', '2'],
   ['5593', '136', '634', ' 312', ' 753', ' 415', '2'],
   ['5594', '136', '643', ' 320', ' 757', ' 415', '2'],
   ['5595', '136', '650', ' 327', ' 759', ' 414', '2'],
   ['5596', '136', '660', ' 335', ' 760', ' 413', '2'],
   ['5597', '136', '669', ' 344', ' 759', ' 411', '2']]},
 {'140': [['5555', '140', '377', ' 108', ' 400', ' 121', '2'],
   ['5556', '140', '378', ' 108', ' 401', ' 122', '2'],
   ['5557', '140', '380', ' 109', ' 403', ' 122', '2'],
   ['5558', '140', '380', ' 110', ' 405', ' 124', '2'],
   ['5560', '140', '379', ' 109', ' 407', ' 126', '2'],
   ['5561', '140', '378', ' 107', ' 408', ' 126', '2'],
   ['5574', '140', '389', ' 113', ' 417', ' 131', '2'],
   ['5575', '140', '389', ' 114', ' 417', ' 132', '2'],
   ['5576', '140', '390', ' 115', ' 417', ' 132', '2'],
   ['5577', '140', '391', ' 115', ' 418', ' 132', '2'],
   ['5578', '140', '392', ' 115', ' 419', ' 132', '2'],
   ['5579', '140', '393', ' 116', ' 419', ' 133', '2'],
   ['5580', '140', '395', ' 116', ' 421', ' 133', '2'],
   ['5581', '140', '394', ' 115', ' 422', ' 133', '2'],
   ['5582', '140', '395', ' 116', ' 422', ' 134', '2'],
   ['5583', '140', '397', ' 116', ' 422', ' 134', '2'],
   ['5584', '140', '398', ' 117', ' 423', ' 135', '2'],
   ['5585', '140', '398', ' 118', ' 424', ' 135', '2'],
   ['5586', '140', '398', ' 118', ' 424', ' 136', '2'],
   ['5587', '140', '399', ' 119', ' 425', ' 138', '2'],
   ['5588', '140', '399', ' 120', ' 426', ' 138', '2'],
   ['5589', '140', '401', ' 120', ' 428', ' 140', '2'],
   ['5590', '140', '402', ' 119', ' 429', ' 139', '2'],
   ['5591', '140', '402', ' 119', ' 430', ' 140', '2'],
   ['5592', '140', '404', ' 120', ' 431', ' 140', '2'],
   ['5593', '140', '403', ' 119', ' 432', ' 141', '2'],
   ['5594', '140', '405', ' 121', ' 432', ' 141', '2'],
   ['5595', '140', '406', ' 122', ' 433', ' 142', '2'],
   ['5596', '140', '407', ' 123', ' 434', ' 143', '2'],
   ['5597', '140', '408', ' 124', ' 433', ' 143', '2'],
   ['5598', '140', '408', ' 124', ' 435', ' 143', '2'],
   ['5599', '140', '408', ' 123', ' 437', ' 145', '2'],
   ['5600', '140', '408', ' 123', ' 438', ' 145', '2'],
   ['5601', '140', '410', ' 124', ' 439', ' 145', '2'],
   ['5602', '140', '411', ' 125', ' 440', ' 146', '2'],
   ['5603', '140', '413', ' 127', ' 440', ' 146', '2'],
   ['5604', '140', '414', ' 129', ' 441', ' 147', '2'],
   ['5605', '140', '414', ' 128', ' 445', ' 149', '2'],
   ['5606', '140', '414', ' 128', ' 447', ' 150', '2'],
   ['5607', '140', '415', ' 128', ' 448', ' 151', '2'],
   ['5608', '140', '416', ' 129', ' 449', ' 152', '2'],
   ['5609', '140', '417', ' 130', ' 449', ' 152', '2'],
   ['5610', '140', '417', ' 130', ' 450', ' 153', '2'],
   ['5611', '140', '417', ' 131', ' 451', ' 154', '2'],
   ['5612', '140', '417', ' 131', ' 452', ' 156', '2'],
   ['5613', '140', '417', ' 132', ' 453', ' 157', '2'],
   ['5614', '140', '419', ' 132', ' 454', ' 157', '2'],
   ['5615', '140', '419', ' 132', ' 455', ' 158', '2'],
   ['5616', '140', '420', ' 134', ' 456', ' 159', '2'],
   ['5617', '140', '420', ' 134', ' 457', ' 161', '2'],
   ['5618', '140', '421', ' 135', ' 459', ' 162', '2'],
   ['5619', '140', '421', ' 135', ' 460', ' 163', '2'],
   ['5620', '140', '422', ' 135', ' 462', ' 164', '2'],
   ['5621', '140', '423', ' 136', ' 463', ' 165', '2'],
   ['5622', '140', '425', ' 138', ' 463', ' 166', '2'],
   ['5623', '140', '426', ' 139', ' 465', ' 167', '2'],
   ['5624', '140', '426', ' 139', ' 466', ' 168', '2'],
   ['5625', '140', '427', ' 140', ' 468', ' 171', '2'],
   ['5626', '140', '426', ' 141', ' 469', ' 172', '2'],
   ['5627', '140', '427', ' 141', ' 471', ' 173', '2'],
   ['5628', '140', '428', ' 142', ' 471', ' 174', '2'],
   ['5629', '140', '431', ' 144', ' 474', ' 176', '2'],
   ['5630', '140', '433', ' 145', ' 475', ' 177', '2'],
   ['5631', '140', '433', ' 146', ' 475', ' 179', '2'],
   ['5632', '140', '433', ' 147', ' 477', ' 181', '2'],
   ['5633', '140', '434', ' 148', ' 479', ' 182', '2'],
   ['5634', '140', '436', ' 150', ' 479', ' 183', '2'],
   ['5635', '140', '435', ' 149', ' 481', ' 185', '2'],
   ['5636', '140', '438', ' 153', ' 480', ' 186', '2'],
   ['5637', '140', '440', ' 156', ' 482', ' 189', '2'],
   ['5638', '140', '442', ' 157', ' 484', ' 190', '2'],
   ['5639', '140', '441', ' 157', ' 486', ' 192', '2'],
   ['5640', '140', '442', ' 158', ' 488', ' 194', '2'],
   ['5641', '140', '443', ' 160', ' 489', ' 196', '2'],
   ['5642', '140', '444', ' 161', ' 491', ' 197', '2'],
   ['5643', '140', '444', ' 161', ' 494', ' 200', '2'],
   ['5644', '140', '446', ' 163', ' 497', ' 203', '2'],
   ['5645', '140', '446', ' 165', ' 498', ' 205', '2'],
   ['5646', '140', '448', ' 167', ' 500', ' 208', '2'],
   ['5647', '140', '449', ' 168', ' 502', ' 210', '2'],
   ['5648', '140', '451', ' 170', ' 505', ' 212', '2'],
   ['5649', '140', '452', ' 172', ' 506', ' 215', '2'],
   ['5650', '140', '453', ' 174', ' 508', ' 217', '2'],
   ['5651', '140', '454', ' 176', ' 510', ' 220', '2'],
   ['5652', '140', '455', ' 178', ' 513', ' 224', '2'],
   ['5653', '140', '456', ' 180', ' 516', ' 227', '2'],
   ['5654', '140', '457', ' 180', ' 519', ' 229', '2'],
   ['5655', '140', '458', ' 182', ' 522', ' 232', '2'],
   ['5656', '140', '460', ' 185', ' 525', ' 237', '2'],
   ['5657', '140', '461', ' 188', ' 527', ' 239', '2'],
   ['5658', '140', '465', ' 191', ' 530', ' 243', '2'],
   ['5659', '140', '466', ' 194', ' 533', ' 246', '2'],
   ['5660', '140', '468', ' 196', ' 537', ' 250', '2'],
   ['5661', '140', '469', ' 198', ' 541', ' 255', '2'],
   ['5662', '140', '471', ' 201', ' 543', ' 258', '2'],
   ['5663', '140', '473', ' 203', ' 547', ' 262', '2'],
   ['5664', '140', '474', ' 206', ' 553', ' 268', '2'],
   ['5665', '140', '477', ' 210', ' 556', ' 272', '2'],
   ['5666', '140', '479', ' 212', ' 561', ' 278', '2'],
   ['5667', '140', '482', ' 217', ' 567', ' 284', '2'],
   ['5668', '140', '485', ' 220', ' 571', ' 288', '2'],
   ['5669', '140', '487', ' 223', ' 577', ' 295', '2'],
   ['5670', '140', '491', ' 228', ' 582', ' 300', '2'],
   ['5671', '140', '493', ' 230', ' 588', ' 307', '2'],
   ['5672', '140', '496', ' 234', ' 594', ' 313', '2'],
   ['5673', '140', '500', ' 240', ' 600', ' 320', '2'],
   ['5674', '140', '503', ' 244', ' 607', ' 328', '2'],
   ['5675', '140', '507', ' 249', ' 614', ' 336', '2'],
   ['5676', '140', '511', ' 254', ' 622', ' 344', '2'],
   ['5677', '140', '516', ' 259', ' 631', ' 352', '2'],
   ['5678', '140', '521', ' 266', ' 639', ' 362', '2'],
   ['5679', '140', '526', ' 272', ' 650', ' 373', '2'],
   ['5680', '140', '530', ' 277', ' 660', ' 384', '2'],
   ['5681', '140', '534', ' 284', ' 671', ' 397', '2'],
   ['5682', '140', '541', ' 292', ' 681', ' 408', '2'],
   ['5683', '140', '551', ' 301', ' 689', ' 414', '2'],
   ['5684', '140', '565', ' 309', ' 700', ' 416', '2'],
   ['5685', '140', '579', ' 317', ' 710', ' 418', '2'],
   ['5686', '140', '589', ' 326', ' 708', ' 414', '2'],
   ['5687', '140', '602', ' 339', ' 709', ' 414', '2'],
   ['5688', '140', '614', ' 349', ' 712', ' 413', '2'],
   ['5689', '140', '628', ' 362', ' 712', ' 412', '2']]},
 {'139': [['5505', '139', '343', ' 106', ' 367', ' 121', '2'],
   ['5506', '139', '343', ' 106', ' 367', ' 121', '2'],
   ['5507', '139', '344', ' 106', ' 368', ' 121', '2'],
   ['5508', '139', '343', ' 106', ' 368', ' 122', '2'],
   ['5509', '139', '344', ' 107', ' 369', ' 122', '2'],
   ['5510', '139', '343', ' 107', ' 370', ' 123', '2'],
   ['5511', '139', '344', ' 107', ' 370', ' 124', '2'],
   ['5512', '139', '343', ' 107', ' 370', ' 124', '2'],
   ['5513', '139', '344', ' 107', ' 370', ' 124', '2'],
   ['5521', '139', '345', ' 107', ' 372', ' 125', '2'],
   ['5522', '139', '345', ' 108', ' 372', ' 125', '2'],
   ['5523', '139', '346', ' 108', ' 371', ' 126', '2'],
   ['5524', '139', '346', ' 108', ' 371', ' 126', '2'],
   ['5525', '139', '346', ' 109', ' 371', ' 126', '2'],
   ['5526', '139', '347', ' 108', ' 372', ' 126', '2'],
   ['5527', '139', '347', ' 109', ' 372', ' 126', '2'],
   ['5528', '139', '348', ' 109', ' 372', ' 126', '2'],
   ['5529', '139', '348', ' 109', ' 373', ' 126', '2'],
   ['5530', '139', '348', ' 109', ' 373', ' 126', '2'],
   ['5531', '139', '348', ' 108', ' 373', ' 126', '2'],
   ['5532', '139', '348', ' 109', ' 373', ' 127', '2'],
   ['5533', '139', '349', ' 109', ' 373', ' 127', '2'],
   ['5534', '139', '348', ' 109', ' 373', ' 127', '2'],
   ['5535', '139', '348', ' 109', ' 373', ' 127', '2'],
   ['5536', '139', '348', ' 109', ' 373', ' 127', '2'],
   ['5537', '139', '348', ' 109', ' 373', ' 127', '2'],
   ['5538', '139', '348', ' 108', ' 374', ' 127', '2'],
   ['5539', '139', '349', ' 109', ' 375', ' 128', '2'],
   ['5540', '139', '349', ' 109', ' 375', ' 128', '2'],
   ['5541', '139', '349', ' 109', ' 375', ' 128', '2'],
   ['5542', '139', '349', ' 109', ' 375', ' 128', '2'],
   ['5543', '139', '350', ' 110', ' 375', ' 128', '2'],
   ['5544', '139', '350', ' 110', ' 375', ' 129', '2'],
   ['5545', '139', '349', ' 110', ' 375', ' 129', '2'],
   ['5546', '139', '349', ' 110', ' 375', ' 130', '2'],
   ['5547', '139', '349', ' 110', ' 376', ' 130', '2'],
   ['5548', '139', '349', ' 110', ' 376', ' 130', '2'],
   ['5550', '139', '351', ' 112', ' 375', ' 131', '2'],
   ['5551', '139', '350', ' 112', ' 375', ' 131', '2'],
   ['5552', '139', '351', ' 112', ' 376', ' 132', '2'],
   ['5553', '139', '351', ' 112', ' 376', ' 132', '2'],
   ['5554', '139', '351', ' 112', ' 377', ' 132', '2'],
   ['5555', '139', '351', ' 113', ' 377', ' 133', '2'],
   ['5556', '139', '352', ' 113', ' 378', ' 133', '2'],
   ['5557', '139', '352', ' 113', ' 379', ' 134', '2'],
   ['5558', '139', '352', ' 113', ' 379', ' 134', '2'],
   ['5559', '139', '353', ' 113', ' 379', ' 134', '2'],
   ['5560', '139', '353', ' 113', ' 380', ' 134', '2'],
   ['5561', '139', '353', ' 113', ' 380', ' 134', '2'],
   ['5562', '139', '353', ' 113', ' 381', ' 135', '2'],
   ['5563', '139', '354', ' 113', ' 381', ' 135', '2'],
   ['5564', '139', '353', ' 112', ' 382', ' 135', '2'],
   ['5565', '139', '353', ' 113', ' 383', ' 136', '2'],
   ['5566', '139', '353', ' 113', ' 384', ' 137', '2'],
   ['5567', '139', '353', ' 112', ' 384', ' 137', '2'],
   ['5570', '139', '354', ' 114', ' 384', ' 139', '2'],
   ['5571', '139', '354', ' 114', ' 384', ' 139', '2'],
   ['5572', '139', '354', ' 114', ' 385', ' 139', '2'],
   ['5573', '139', '355', ' 114', ' 386', ' 140', '2'],
   ['5574', '139', '354', ' 115', ' 386', ' 140', '2'],
   ['5575', '139', '355', ' 115', ' 386', ' 141', '2'],
   ['5576', '139', '353', ' 115', ' 386', ' 141', '2'],
   ['5577', '139', '354', ' 115', ' 386', ' 141', '2'],
   ['5578', '139', '354', ' 115', ' 385', ' 141', '2'],
   ['5579', '139', '354', ' 115', ' 386', ' 142', '2'],
   ['5580', '139', '354', ' 115', ' 385', ' 142', '2'],
   ['5581', '139', '354', ' 115', ' 386', ' 142', '2'],
   ['5582', '139', '354', ' 115', ' 386', ' 143', '2'],
   ['5583', '139', '355', ' 116', ' 386', ' 143', '2'],
   ['5584', '139', '355', ' 117', ' 385', ' 144', '2'],
   ['5585', '139', '356', ' 118', ' 384', ' 144', '2'],
   ['5586', '139', '357', ' 119', ' 384', ' 144', '2'],
   ['5587', '139', '357', ' 120', ' 384', ' 145', '2'],
   ['5588', '139', '358', ' 121', ' 385', ' 146', '2'],
   ['5589', '139', '358', ' 122', ' 385', ' 146', '2'],
   ['5590', '139', '358', ' 123', ' 385', ' 147', '2'],
   ['5591', '139', '358', ' 124', ' 384', ' 147', '2'],
   ['5592', '139', '358', ' 125', ' 384', ' 148', '2'],
   ['5593', '139', '359', ' 126', ' 384', ' 148', '2'],
   ['5594', '139', '359', ' 126', ' 385', ' 148', '2'],
   ['5595', '139', '359', ' 126', ' 385', ' 149', '2'],
   ['5596', '139', '358', ' 127', ' 386', ' 150', '2'],
   ['5597', '139', '358', ' 127', ' 387', ' 150', '2'],
   ['5598', '139', '357', ' 126', ' 387', ' 151', '2'],
   ['5599', '139', '358', ' 127', ' 387', ' 151', '2'],
   ['5600', '139', '357', ' 127', ' 387', ' 151', '2'],
   ['5601', '139', '357', ' 127', ' 388', ' 152', '2'],
   ['5602', '139', '357', ' 127', ' 388', ' 152', '2'],
   ['5603', '139', '357', ' 127', ' 388', ' 152', '2'],
   ['5604', '139', '358', ' 128', ' 388', ' 153', '2'],
   ['5605', '139', '357', ' 128', ' 389', ' 154', '2'],
   ['5606', '139', '358', ' 129', ' 389', ' 154', '2'],
   ['5607', '139', '358', ' 129', ' 390', ' 155', '2'],
   ['5608', '139', '358', ' 130', ' 390', ' 155', '2'],
   ['5609', '139', '357', ' 130', ' 391', ' 157', '2'],
   ['5610', '139', '357', ' 130', ' 391', ' 157', '2'],
   ['5611', '139', '358', ' 132', ' 392', ' 159', '2'],
   ['5612', '139', '359', ' 133', ' 392', ' 159', '2'],
   ['5613', '139', '359', ' 133', ' 393', ' 160', '2'],
   ['5614', '139', '359', ' 134', ' 393', ' 161', '2'],
   ['5615', '139', '359', ' 134', ' 394', ' 162', '2'],
   ['5616', '139', '360', ' 135', ' 394', ' 163', '2'],
   ['5617', '139', '360', ' 136', ' 396', ' 164', '2'],
   ['5618', '139', '359', ' 136', ' 397', ' 165', '2'],
   ['5619', '139', '359', ' 136', ' 397', ' 166', '2'],
   ['5620', '139', '358', ' 136', ' 397', ' 166', '2'],
   ['5621', '139', '359', ' 136', ' 398', ' 167', '2'],
   ['5622', '139', '359', ' 137', ' 398', ' 168', '2'],
   ['5623', '139', '359', ' 137', ' 398', ' 169', '2'],
   ['5624', '139', '359', ' 138', ' 398', ' 170', '2'],
   ['5625', '139', '359', ' 138', ' 399', ' 171', '2'],
   ['5626', '139', '359', ' 138', ' 400', ' 172', '2'],
   ['5627', '139', '359', ' 139', ' 400', ' 173', '2'],
   ['5628', '139', '359', ' 139', ' 401', ' 173', '2'],
   ['5629', '139', '360', ' 139', ' 401', ' 174', '2'],
   ['5630', '139', '359', ' 140', ' 402', ' 176', '2'],
   ['5631', '139', '360', ' 140', ' 402', ' 177', '2'],
   ['5632', '139', '361', ' 143', ' 401', ' 178', '2'],
   ['5633', '139', '360', ' 144', ' 401', ' 179', '2'],
   ['5634', '139', '360', ' 144', ' 402', ' 180', '2'],
   ['5635', '139', '360', ' 145', ' 402', ' 182', '2'],
   ['5636', '139', '360', ' 146', ' 402', ' 182', '2'],
   ['5637', '139', '361', ' 147', ' 403', ' 183', '2'],
   ['5638', '139', '361', ' 148', ' 404', ' 184', '2'],
   ['5639', '139', '361', ' 148', ' 404', ' 186', '2'],
   ['5640', '139', '360', ' 148', ' 405', ' 187', '2'],
   ['5641', '139', '360', ' 149', ' 406', ' 189', '2'],
   ['5642', '139', '361', ' 151', ' 406', ' 190', '2'],
   ['5643', '139', '362', ' 152', ' 407', ' 191', '2'],
   ['5644', '139', '363', ' 153', ' 409', ' 193', '2'],
   ['5645', '139', '364', ' 154', ' 409', ' 194', '2'],
   ['5646', '139', '364', ' 156', ' 409', ' 195', '2'],
   ['5647', '139', '363', ' 157', ' 410', ' 197', '2'],
   ['5648', '139', '363', ' 158', ' 410', ' 199', '2'],
   ['5649', '139', '363', ' 159', ' 411', ' 200', '2'],
   ['5650', '139', '364', ' 160', ' 412', ' 202', '2'],
   ['5651', '139', '365', ' 161', ' 413', ' 203', '2'],
   ['5652', '139', '365', ' 163', ' 414', ' 205', '2'],
   ['5653', '139', '365', ' 164', ' 415', ' 207', '2'],
   ['5654', '139', '365', ' 164', ' 417', ' 209', '2'],
   ['5655', '139', '365', ' 165', ' 418', ' 211', '2'],
   ['5656', '139', '365', ' 166', ' 418', ' 212', '2'],
   ['5657', '139', '366', ' 167', ' 419', ' 213', '2'],
   ['5658', '139', '367', ' 168', ' 420', ' 215', '2'],
   ['5659', '139', '368', ' 170', ' 421', ' 217', '2'],
   ['5660', '139', '368', ' 172', ' 423', ' 220', '2'],
   ['5661', '139', '368', ' 173', ' 424', ' 224', '2'],
   ['5662', '139', '368', ' 175', ' 425', ' 226', '2'],
   ['5663', '139', '370', ' 176', ' 427', ' 227', '2'],
   ['5664', '139', '371', ' 177', ' 428', ' 228', '2'],
   ['5665', '139', '371', ' 178', ' 430', ' 230', '2'],
   ['5666', '139', '371', ' 180', ' 431', ' 233', '2'],
   ['5667', '139', '371', ' 182', ' 432', ' 237', '2'],
   ['5668', '139', '371', ' 183', ' 434', ' 239', '2'],
   ['5669', '139', '373', ' 186', ' 435', ' 242', '2'],
   ['5670', '139', '373', ' 187', ' 438', ' 245', '2'],
   ['5671', '139', '373', ' 189', ' 441', ' 250', '2'],
   ['5672', '139', '375', ' 192', ' 443', ' 253', '2'],
   ['5673', '139', '376', ' 194', ' 443', ' 255', '2'],
   ['5674', '139', '377', ' 196', ' 445', ' 257', '2'],
   ['5675', '139', '379', ' 199', ' 448', ' 261', '2'],
   ['5676', '139', '380', ' 200', ' 451', ' 264', '2'],
   ['5677', '139', '381', ' 202', ' 453', ' 268', '2'],
   ['5678', '139', '382', ' 204', ' 455', ' 271', '2'],
   ['5679', '139', '383', ' 206', ' 458', ' 274', '2'],
   ['5680', '139', '383', ' 208', ' 459', ' 278', '2'],
   ['5681', '139', '384', ' 210', ' 463', ' 282', '2'],
   ['5682', '139', '386', ' 213', ' 467', ' 287', '2'],
   ['5683', '139', '388', ' 215', ' 468', ' 289', '2'],
   ['5684', '139', '390', ' 218', ' 471', ' 293', '2'],
   ['5685', '139', '390', ' 219', ' 474', ' 298', '2'],
   ['5688', '139', '393', ' 225', ' 485', ' 313', '2'],
   ['5689', '139', '394', ' 227', ' 490', ' 319', '2'],
   ['5690', '139', '395', ' 229', ' 495', ' 325', '2'],
   ['5691', '139', '397', ' 233', ' 497', ' 329', '2'],
   ['5692', '139', '399', ' 239', ' 502', ' 337', '2'],
   ['5693', '139', '402', ' 243', ' 506', ' 342', '2'],
   ['5694', '139', '404', ' 247', ' 511', ' 348', '2'],
   ['5695', '139', '407', ' 252', ' 517', ' 356', '2'],
   ['5696', '139', '408', ' 255', ' 522', ' 363', '2'],
   ['5697', '139', '410', ' 260', ' 528', ' 371', '2'],
   ['5698', '139', '413', ' 265', ' 535', ' 380', '2'],
   ['5699', '139', '414', ' 268', ' 542', ' 389', '2'],
   ['5700', '139', '414', ' 274', ' 550', ' 403', '2'],
   ['5701', '139', '418', ' 279', ' 557', ' 409', '2'],
   ['5702', '139', '425', ' 284', ' 563', ' 412', '2'],
   ['5703', '139', '433', ' 290', ' 566', ' 413', '2'],
   ['5704', '139', '440', ' 297', ' 572', ' 416', '2'],
   ['5705', '139', '446', ' 303', ' 575', ' 415', '2'],
   ['5706', '139', '453', ' 310', ' 579', ' 416', '2'],
   ['5707', '139', '461', ' 318', ' 581', ' 416', '2'],
   ['5708', '139', '470', ' 324', ' 584', ' 414', '2'],
   ['5709', '139', '477', ' 330', ' 590', ' 414', '2'],
   ['5710', '139', '484', ' 342', ' 587', ' 413', '2'],
   ['5711', '139', '494', ' 351', ' 587', ' 411', '2']]},
 {'153': [['6473', '153', '351', ' 118', ' 377', ' 135', '2'],
   ['6474', '153', '350', ' 116', ' 378', ' 135', '2'],
   ['6475', '153', '350', ' 116', ' 378', ' 135', '2'],
   ['6477', '153', '352', ' 118', ' 378', ' 135', '2'],
   ['6478', '153', '350', ' 118', ' 379', ' 137', '2'],
   ['6481', '153', '350', ' 118', ' 380', ' 138', '2'],
   ['6482', '153', '349', ' 118', ' 382', ' 139', '2'],
   ['6483', '153', '348', ' 118', ' 383', ' 141', '2'],
   ['6484', '153', '347', ' 117', ' 384', ' 142', '2'],
   ['6494', '153', '351', ' 123', ' 384', ' 145', '2'],
   ['6496', '153', '356', ' 129', ' 384', ' 147', '2'],
   ['6497', '153', '355', ' 131', ' 385', ' 150', '2'],
   ['6498', '153', '353', ' 128', ' 387', ' 151', '2'],
   ['6499', '153', '352', ' 127', ' 389', ' 151', '2'],
   ['6500', '153', '351', ' 128', ' 389', ' 152', '2'],
   ['6501', '153', '352', ' 128', ' 389', ' 153', '2'],
   ['6504', '153', '352', ' 130', ' 389', ' 154', '2'],
   ['6506', '153', '353', ' 131', ' 390', ' 156', '2'],
   ['6508', '153', '352', ' 132', ' 392', ' 159', '2'],
   ['6509', '153', '354', ' 135', ' 393', ' 162', '2'],
   ['6510', '153', '355', ' 136', ' 395', ' 163', '2'],
   ['6511', '153', '355', ' 137', ' 397', ' 165', '2'],
   ['6512', '153', '354', ' 137', ' 398', ' 167', '2'],
   ['6513', '153', '354', ' 137', ' 399', ' 168', '2'],
   ['6514', '153', '353', ' 136', ' 400', ' 169', '2'],
   ['6515', '153', '353', ' 137', ' 399', ' 170', '2'],
   ['6516', '153', '352', ' 137', ' 400', ' 171', '2'],
   ['6517', '153', '352', ' 138', ' 399', ' 172', '2'],
   ['6518', '153', '353', ' 139', ' 400', ' 173', '2'],
   ['6519', '153', '354', ' 140', ' 400', ' 175', '2'],
   ['6520', '153', '354', ' 141', ' 400', ' 176', '2'],
   ['6521', '153', '353', ' 142', ' 401', ' 179', '2'],
   ['6522', '153', '354', ' 144', ' 401', ' 180', '2'],
   ['6523', '153', '354', ' 145', ' 401', ' 182', '2'],
   ['6524', '153', '355', ' 147', ' 401', ' 184', '2'],
   ['6525', '153', '355', ' 149', ' 401', ' 186', '2'],
   ['6526', '153', '356', ' 150', ' 402', ' 187', '2'],
   ['6527', '153', '357', ' 151', ' 403', ' 188', '2'],
   ['6528', '153', '357', ' 152', ' 404', ' 190', '2'],
   ['6529', '153', '358', ' 153', ' 406', ' 192', '2'],
   ['6530', '153', '359', ' 156', ' 406', ' 194', '2'],
   ['6531', '153', '357', ' 155', ' 408', ' 198', '2'],
   ['6532', '153', '357', ' 155', ' 410', ' 200', '2'],
   ['6533', '153', '358', ' 155', ' 413', ' 201', '2'],
   ['6534', '153', '360', ' 158', ' 414', ' 204', '2'],
   ['6535', '153', '360', ' 159', ' 415', ' 206', '2'],
   ['6536', '153', '361', ' 162', ' 415', ' 208', '2'],
   ['6537', '153', '362', ' 164', ' 416', ' 210', '2'],
   ['6538', '153', '362', ' 165', ' 418', ' 214', '2'],
   ['6539', '153', '362', ' 167', ' 420', ' 217', '2'],
   ['6540', '153', '361', ' 167', ' 422', ' 220', '2'],
   ['6541', '153', '362', ' 170', ' 423', ' 223', '2'],
   ['6542', '153', '363', ' 173', ' 424', ' 226', '2'],
   ['6543', '153', '363', ' 174', ' 425', ' 229', '2'],
   ['6544', '153', '364', ' 176', ' 427', ' 232', '2'],
   ['6545', '153', '366', ' 177', ' 430', ' 234', '2'],
   ['6546', '153', '366', ' 179', ' 432', ' 238', '2'],
   ['6547', '153', '367', ' 183', ' 433', ' 242', '2'],
   ['6548', '153', '367', ' 184', ' 436', ' 246', '2'],
   ['6549', '153', '367', ' 188', ' 438', ' 251', '2'],
   ['6550', '153', '370', ' 193', ' 440', ' 256', '2'],
   ['6551', '153', '369', ' 192', ' 444', ' 260', '2'],
   ['6552', '153', '370', ' 194', ' 447', ' 264', '2'],
   ['6553', '153', '371', ' 198', ' 450', ' 269', '2'],
   ['6554', '153', '372', ' 201', ' 454', ' 275', '2'],
   ['6555', '153', '373', ' 203', ' 457', ' 279', '2'],
   ['6556', '153', '375', ' 208', ' 460', ' 285', '2'],
   ['6557', '153', '375', ' 210', ' 463', ' 290', '2'],
   ['6558', '153', '377', ' 214', ' 467', ' 298', '2'],
   ['6559', '153', '379', ' 220', ' 472', ' 305', '2'],
   ['6560', '153', '380', ' 224', ' 476', ' 312', '2'],
   ['6561', '153', '381', ' 228', ' 481', ' 319', '2'],
   ['6562', '153', '383', ' 233', ' 485', ' 328', '2'],
   ['6563', '153', '385', ' 238', ' 491', ' 336', '2'],
   ['6564', '153', '387', ' 244', ' 497', ' 345', '2'],
   ['6565', '153', '389', ' 248', ' 504', ' 355', '2'],
   ['6566', '153', '391', ' 254', ' 511', ' 365', '2'],
   ['6567', '153', '393', ' 261', ' 519', ' 377', '2'],
   ['6568', '153', '396', ' 268', ' 526', ' 389', '2'],
   ['6569', '153', '397', ' 275', ' 535', ' 404', '2'],
   ['6570', '153', '402', ' 282', ' 541', ' 411', '2'],
   ['6571', '153', '410', ' 290', ' 545', ' 415', '2'],
   ['6572', '153', '421', ' 300', ' 552', ' 418', '2'],
   ['6573', '153', '430', ' 309', ' 554', ' 416', '2'],
   ['6575', '153', '446', ' 326', ' 556', ' 416', '2'],
   ['6576', '153', '457', ' 342', ' 552', ' 414', '2']]},
 {'154': [['6626', '154', '370', ' 107', ' 393', ' 122', '2'],
   ['6627', '154', '372', ' 108', ' 394', ' 123', '2'],
   ['6628', '154', '371', ' 107', ' 395', ' 123', '2'],
   ['6630', '154', '371', ' 108', ' 395', ' 123', '2'],
   ['6631', '154', '371', ' 108', ' 396', ' 124', '2'],
   ['6632', '154', '371', ' 108', ' 397', ' 125', '2'],
   ['6633', '154', '371', ' 108', ' 397', ' 125', '2'],
   ['6634', '154', '371', ' 108', ' 398', ' 125', '2'],
   ['6635', '154', '371', ' 109', ' 398', ' 126', '2'],
   ['6636', '154', '372', ' 109', ' 398', ' 126', '2'],
   ['6637', '154', '372', ' 109', ' 398', ' 126', '2'],
   ['6638', '154', '372', ' 109', ' 399', ' 126', '2'],
   ['6639', '154', '373', ' 110', ' 399', ' 127', '2'],
   ['6640', '154', '373', ' 110', ' 400', ' 127', '2'],
   ['6641', '154', '373', ' 110', ' 400', ' 127', '2'],
   ['6642', '154', '373', ' 110', ' 400', ' 127', '2'],
   ['6646', '154', '373', ' 110', ' 401', ' 127', '2'],
   ['6655', '154', '376', ' 115', ' 404', ' 132', '2'],
   ['6656', '154', '378', ' 116', ' 404', ' 133', '2'],
   ['6659', '154', '377', ' 116', ' 406', ' 134', '2'],
   ['6660', '154', '378', ' 116', ' 406', ' 134', '2'],
   ['6661', '154', '378', ' 117', ' 406', ' 134', '2'],
   ['6663', '154', '379', ' 116', ' 408', ' 135', '2'],
   ['6664', '154', '377', ' 114', ' 409', ' 135', '2'],
   ['6665', '154', '377', ' 115', ' 410', ' 136', '2'],
   ['6666', '154', '378', ' 115', ' 411', ' 137', '2'],
   ['6667', '154', '378', ' 115', ' 411', ' 137', '2'],
   ['6668', '154', '379', ' 115', ' 411', ' 138', '2'],
   ['6669', '154', '379', ' 117', ' 411', ' 138', '2'],
   ['6670', '154', '380', ' 117', ' 411', ' 139', '2'],
   ['6671', '154', '381', ' 118', ' 411', ' 139', '2'],
   ['6672', '154', '382', ' 118', ' 412', ' 139', '2'],
   ['6673', '154', '382', ' 118', ' 412', ' 140', '2'],
   ['6674', '154', '383', ' 119', ' 412', ' 140', '2'],
   ['6675', '154', '384', ' 120', ' 412', ' 140', '2'],
   ['6676', '154', '384', ' 120', ' 413', ' 140', '2'],
   ['6677', '154', '384', ' 118', ' 415', ' 141', '2'],
   ['6678', '154', '383', ' 118', ' 415', ' 141', '2'],
   ['6679', '154', '383', ' 118', ' 415', ' 142', '2'],
   ['6680', '154', '383', ' 119', ' 417', ' 143', '2'],
   ['6681', '154', '385', ' 121', ' 417', ' 144', '2'],
   ['6682', '154', '387', ' 123', ' 416', ' 145', '2'],
   ['6683', '154', '388', ' 126', ' 416', ' 145', '2'],
   ['6684', '154', '389', ' 127', ' 416', ' 146', '2'],
   ['6685', '154', '389', ' 127', ' 417', ' 147', '2'],
   ['6686', '154', '388', ' 126', ' 418', ' 147', '2'],
   ['6687', '154', '389', ' 127', ' 417', ' 147', '2'],
   ['6688', '154', '389', ' 127', ' 419', ' 147', '2'],
   ['6689', '154', '390', ' 127', ' 420', ' 148', '2'],
   ['6690', '154', '389', ' 128', ' 421', ' 149', '2'],
   ['6691', '154', '389', ' 126', ' 422', ' 150', '2'],
   ['6692', '154', '389', ' 126', ' 423', ' 150', '2'],
   ['6693', '154', '390', ' 128', ' 424', ' 151', '2'],
   ['6694', '154', '388', ' 126', ' 425', ' 152', '2'],
   ['6695', '154', '389', ' 127', ' 426', ' 152', '2'],
   ['6696', '154', '389', ' 127', ' 427', ' 153', '2'],
   ['6697', '154', '390', ' 127', ' 428', ' 154', '2'],
   ['6698', '154', '390', ' 127', ' 428', ' 154', '2'],
   ['6699', '154', '391', ' 127', ' 430', ' 155', '2'],
   ['6700', '154', '392', ' 128', ' 430', ' 156', '2'],
   ['6701', '154', '393', ' 128', ' 432', ' 157', '2'],
   ['6702', '154', '392', ' 128', ' 432', ' 158', '2'],
   ['6703', '154', '393', ' 128', ' 432', ' 158', '2'],
   ['6704', '154', '393', ' 128', ' 434', ' 159', '2'],
   ['6705', '154', '393', ' 128', ' 435', ' 160', '2'],
   ['6706', '154', '395', ' 130', ' 436', ' 161', '2'],
   ['6707', '154', '396', ' 130', ' 437', ' 162', '2'],
   ['6708', '154', '396', ' 130', ' 439', ' 163', '2'],
   ['6709', '154', '396', ' 130', ' 440', ' 164', '2'],
   ['6710', '154', '397', ' 131', ' 440', ' 165', '2'],
   ['6711', '154', '397', ' 131', ' 442', ' 167', '2'],
   ['6712', '154', '398', ' 132', ' 442', ' 168', '2'],
   ['6713', '154', '398', ' 132', ' 444', ' 170', '2'],
   ['6714', '154', '398', ' 133', ' 444', ' 171', '2'],
   ['6715', '154', '400', ' 135', ' 444', ' 171', '2'],
   ['6716', '154', '400', ' 135', ' 445', ' 172', '2'],
   ['6717', '154', '403', ' 137', ' 445', ' 173', '2'],
   ['6718', '154', '403', ' 138', ' 446', ' 173', '2'],
   ['6719', '154', '404', ' 137', ' 448', ' 174', '2'],
   ['6720', '154', '405', ' 137', ' 449', ' 175', '2'],
   ['6721', '154', '405', ' 138', ' 451', ' 177', '2'],
   ['6722', '154', '406', ' 139', ' 451', ' 178', '2'],
   ['6723', '154', '406', ' 140', ' 454', ' 180', '2'],
   ['6724', '154', '408', ' 141', ' 456', ' 182', '2'],
   ['6725', '154', '409', ' 142', ' 457', ' 183', '2'],
   ['6726', '154', '410', ' 144', ' 458', ' 185', '2'],
   ['6727', '154', '411', ' 145', ' 459', ' 185', '2'],
   ['6728', '154', '412', ' 145', ' 460', ' 186', '2'],
   ['6729', '154', '412', ' 146', ' 462', ' 188', '2'],
   ['6730', '154', '414', ' 147', ' 463', ' 189', '2'],
   ['6731', '154', '414', ' 147', ' 464', ' 190', '2'],
   ['6732', '154', '416', ' 148', ' 466', ' 191', '2'],
   ['6733', '154', '416', ' 149', ' 467', ' 193', '2'],
   ['6734', '154', '417', ' 150', ' 469', ' 195', '2'],
   ['6735', '154', '418', ' 151', ' 471', ' 197', '2'],
   ['6736', '154', '419', ' 151', ' 472', ' 198', '2'],
   ['6738', '154', '421', ' 154', ' 475', ' 202', '2'],
   ['6739', '154', '423', ' 155', ' 478', ' 204', '2'],
   ['6740', '154', '424', ' 157', ' 479', ' 206', '2'],
   ['6741', '154', '426', ' 159', ' 481', ' 207', '2'],
   ['6742', '154', '426', ' 160', ' 483', ' 210', '2'],
   ['6743', '154', '427', ' 160', ' 485', ' 212', '2'],
   ['6744', '154', '428', ' 161', ' 487', ' 213', '2'],
   ['6745', '154', '429', ' 163', ' 490', ' 217', '2'],
   ['6746', '154', '431', ' 164', ' 493', ' 219', '2'],
   ['6747', '154', '432', ' 165', ' 494', ' 220', '2'],
   ['6748', '154', '433', ' 166', ' 496', ' 222', '2'],
   ['6749', '154', '434', ' 167', ' 498', ' 224', '2'],
   ['6750', '154', '435', ' 168', ' 501', ' 227', '2'],
   ['6751', '154', '437', ' 169', ' 504', ' 229', '2'],
   ['6752', '154', '438', ' 171', ' 507', ' 232', '2'],
   ['6753', '154', '441', ' 173', ' 510', ' 236', '2'],
   ['6754', '154', '444', ' 175', ' 512', ' 237', '2'],
   ['6755', '154', '445', ' 177', ' 516', ' 240', '2'],
   ['6756', '154', '446', ' 178', ' 520', ' 245', '2'],
   ['6757', '154', '448', ' 182', ' 522', ' 249', '2'],
   ['6758', '154', '450', ' 183', ' 526', ' 252', '2'],
   ['6759', '154', '451', ' 184', ' 529', ' 255', '2'],
   ['6760', '154', '455', ' 190', ' 531', ' 258', '2'],
   ['6761', '154', '457', ' 192', ' 535', ' 262', '2'],
   ['6762', '154', '459', ' 192', ' 540', ' 265', '2'],
   ['6763', '154', '459', ' 193', ' 545', ' 270', '2'],
   ['6764', '154', '462', ' 195', ' 551', ' 276', '2'],
   ['6765', '154', '464', ' 197', ' 554', ' 279', '2'],
   ['6766', '154', '467', ' 198', ' 556', ' 279', '2'],
   ['6767', '154', '469', ' 200', ' 562', ' 285', '2'],
   ['6768', '154', '472', ' 202', ' 567', ' 289', '2'],
   ['6769', '154', '474', ' 204', ' 571', ' 292', '2'],
   ['6770', '154', '478', ' 209', ' 577', ' 299', '2'],
   ['6771', '154', '481', ' 213', ' 583', ' 306', '2'],
   ['6773', '154', '487', ' 219', ' 592', ' 315', '2'],
   ['6774', '154', '491', ' 222', ' 600', ' 322', '2'],
   ['6775', '154', '494', ' 225', ' 607', ' 329', '2'],
   ['6777', '154', '500', ' 232', ' 619', ' 342', '2'],
   ['6778', '154', '506', ' 238', ' 627', ' 348', '2'],
   ['6779', '154', '511', ' 241', ' 637', ' 356', '2'],
   ['6780', '154', '515', ' 245', ' 645', ' 365', '2'],
   ['6781', '154', '520', ' 250', ' 654', ' 373', '2'],
   ['6782', '154', '524', ' 253', ' 664', ' 382', '2'],
   ['6783', '154', '528', ' 258', ' 675', ' 394', '2'],
   ['6784', '154', '533', ' 264', ' 685', ' 405', '2'],
   ['6785', '154', '540', ' 269', ' 694', ' 412', '2'],
   ['6786', '154', '550', ' 276', ' 702', ' 416', '2'],
   ['6787', '154', '562', ' 281', ' 712', ' 417', '2'],
   ['6788', '154', '571', ' 288', ' 718', ' 418', '2'],
   ['6789', '154', '580', ' 295', ' 720', ' 416', '2'],
   ['6790', '154', '589', ' 302', ' 722', ' 413', '2'],
   ['6791', '154', '600', ' 310', ' 729', ' 415', '2'],
   ['6792', '154', '611', ' 318', ' 735', ' 413', '2'],
   ['6793', '154', '621', ' 325', ' 741', ' 413', '2'],
   ['6794', '154', '631', ' 336', ' 746', ' 415', '2'],
   ['6795', '154', '641', ' 344', ' 746', ' 412', '2']]},
 {'166': [['7644', '166', '380', ' 108', ' 404', ' 126', '2'],
   ['7645', '166', '380', ' 108', ' 404', ' 127', '2'],
   ['7646', '166', '380', ' 108', ' 405', ' 127', '2'],
   ['7647', '166', '381', ' 108', ' 405', ' 128', '2'],
   ['7648', '166', '381', ' 109', ' 406', ' 128', '2'],
   ['7649', '166', '381', ' 109', ' 406', ' 129', '2'],
   ['7650', '166', '382', ' 110', ' 405', ' 128', '2'],
   ['7651', '166', '382', ' 111', ' 405', ' 128', '2'],
   ['7652', '166', '382', ' 111', ' 405', ' 128', '2'],
   ['7653', '166', '382', ' 111', ' 404', ' 128', '2'],
   ['7658', '166', '382', ' 111', ' 405', ' 128', '2'],
   ['7682', '166', '386', ' 115', ' 409', ' 133', '2'],
   ['7687', '166', '386', ' 116', ' 411', ' 136', '2'],
   ['7688', '166', '386', ' 116', ' 412', ' 136', '2'],
   ['7689', '166', '385', ' 115', ' 413', ' 137', '2'],
   ['7691', '166', '385', ' 115', ' 414', ' 138', '2'],
   ['7692', '166', '385', ' 115', ' 414', ' 139', '2'],
   ['7693', '166', '386', ' 115', ' 415', ' 139', '2'],
   ['7694', '166', '386', ' 115', ' 415', ' 139', '2'],
   ['7695', '166', '386', ' 115', ' 415', ' 139', '2'],
   ['7696', '166', '387', ' 116', ' 414', ' 140', '2'],
   ['7697', '166', '387', ' 116', ' 414', ' 140', '2'],
   ['7698', '166', '387', ' 117', ' 414', ' 140', '2'],
   ['7699', '166', '388', ' 117', ' 415', ' 140', '2'],
   ['7700', '166', '389', ' 118', ' 415', ' 140', '2'],
   ['7701', '166', '390', ' 120', ' 415', ' 141', '2'],
   ['7702', '166', '390', ' 120', ' 416', ' 141', '2'],
   ['7703', '166', '390', ' 121', ' 416', ' 142', '2'],
   ['7704', '166', '390', ' 119', ' 417', ' 142', '2'],
   ['7705', '166', '390', ' 120', ' 418', ' 142', '2'],
   ['7706', '166', '390', ' 120', ' 418', ' 143', '2'],
   ['7707', '166', '390', ' 121', ' 419', ' 143', '2'],
   ['7708', '166', '390', ' 121', ' 419', ' 144', '2'],
   ['7709', '166', '390', ' 121', ' 420', ' 145', '2'],
   ['7710', '166', '390', ' 121', ' 420', ' 145', '2'],
   ['7711', '166', '390', ' 121', ' 420', ' 145', '2'],
   ['7712', '166', '390', ' 121', ' 420', ' 146', '2'],
   ['7713', '166', '390', ' 122', ' 421', ' 147', '2'],
   ['7714', '166', '391', ' 123', ' 421', ' 147', '2'],
   ['7715', '166', '392', ' 123', ' 421', ' 147', '2'],
   ['7716', '166', '393', ' 124', ' 421', ' 147', '2'],
   ['7717', '166', '393', ' 125', ' 421', ' 147', '2'],
   ['7718', '166', '394', ' 126', ' 422', ' 148', '2'],
   ['7719', '166', '394', ' 127', ' 422', ' 149', '2'],
   ['7720', '166', '394', ' 128', ' 423', ' 150', '2'],
   ['7721', '166', '394', ' 128', ' 424', ' 151', '2'],
   ['7722', '166', '394', ' 128', ' 425', ' 151', '2'],
   ['7723', '166', '394', ' 128', ' 425', ' 151', '2'],
   ['7724', '166', '395', ' 129', ' 425', ' 152', '2'],
   ['7725', '166', '396', ' 129', ' 426', ' 152', '2'],
   ['7726', '166', '396', ' 130', ' 426', ' 152', '2'],
   ['7727', '166', '396', ' 130', ' 426', ' 153', '2'],
   ['7728', '166', '396', ' 130', ' 427', ' 153', '2'],
   ['7729', '166', '397', ' 130', ' 428', ' 153', '2'],
   ['7730', '166', '397', ' 131', ' 429', ' 154', '2'],
   ['7731', '166', '397', ' 131', ' 429', ' 155', '2'],
   ['7732', '166', '397', ' 131', ' 431', ' 156', '2'],
   ['7733', '166', '398', ' 132', ' 432', ' 157', '2'],
   ['7734', '166', '398', ' 132', ' 434', ' 158', '2'],
   ['7735', '166', '398', ' 132', ' 434', ' 159', '2'],
   ['7736', '166', '399', ' 133', ' 434', ' 159', '2'],
   ['7737', '166', '399', ' 134', ' 435', ' 160', '2'],
   ['7738', '166', '400', ' 134', ' 435', ' 160', '2'],
   ['7739', '166', '400', ' 134', ' 435', ' 160', '2'],
   ['7740', '166', '401', ' 135', ' 436', ' 161', '2'],
   ['7741', '166', '400', ' 135', ' 437', ' 162', '2'],
   ['7742', '166', '400', ' 134', ' 439', ' 163', '2'],
   ['7743', '166', '400', ' 134', ' 439', ' 164', '2'],
   ['7744', '166', '401', ' 135', ' 440', ' 164', '2'],
   ['7745', '166', '401', ' 136', ' 441', ' 165', '2'],
   ['7746', '166', '402', ' 136', ' 441', ' 166', '2'],
   ['7747', '166', '402', ' 136', ' 441', ' 166', '2'],
   ['7748', '166', '404', ' 138', ' 442', ' 166', '2'],
   ['7749', '166', '404', ' 138', ' 444', ' 168', '2'],
   ['7750', '166', '405', ' 138', ' 446', ' 169', '2'],
   ['7751', '166', '406', ' 139', ' 446', ' 170', '2'],
   ['7752', '166', '407', ' 140', ' 447', ' 170', '2'],
   ['7753', '166', '408', ' 141', ' 447', ' 171', '2'],
   ['7754', '166', '408', ' 142', ' 448', ' 172', '2'],
   ['7755', '166', '409', ' 143', ' 448', ' 173', '2'],
   ['7756', '166', '409', ' 143', ' 449', ' 174', '2'],
   ['7757', '166', '409', ' 143', ' 450', ' 174', '2'],
   ['7758', '166', '409', ' 143', ' 451', ' 175', '2'],
   ['7759', '166', '411', ' 145', ' 451', ' 176', '2'],
   ['7760', '166', '411', ' 145', ' 452', ' 177', '2'],
   ['7761', '166', '412', ' 146', ' 454', ' 178', '2'],
   ['7762', '166', '412', ' 146', ' 455', ' 179', '2'],
   ['7763', '166', '413', ' 147', ' 456', ' 180', '2'],
   ['7764', '166', '413', ' 148', ' 456', ' 181', '2'],
   ['7765', '166', '414', ' 149', ' 457', ' 182', '2'],
   ['7766', '166', '415', ' 149', ' 460', ' 184', '2'],
   ['7767', '166', '415', ' 149', ' 461', ' 185', '2'],
   ['7768', '166', '415', ' 149', ' 462', ' 186', '2'],
   ['7769', '166', '415', ' 149', ' 463', ' 187', '2'],
   ['7770', '166', '416', ' 150', ' 464', ' 188', '2'],
   ['7771', '166', '418', ' 151', ' 465', ' 189', '2'],
   ['7772', '166', '419', ' 152', ' 466', ' 190', '2'],
   ['7773', '166', '420', ' 152', ' 467', ' 190', '2'],
   ['7774', '166', '420', ' 153', ' 469', ' 193', '2'],
   ['7775', '166', '421', ' 154', ' 470', ' 194', '2'],
   ['7776', '166', '422', ' 156', ' 470', ' 196', '2'],
   ['7777', '166', '423', ' 157', ' 472', ' 197', '2'],
   ['7778', '166', '424', ' 158', ' 474', ' 199', '2'],
   ['7779', '166', '424', ' 158', ' 476', ' 201', '2'],
   ['7780', '166', '425', ' 159', ' 477', ' 202', '2'],
   ['7781', '166', '426', ' 160', ' 478', ' 204', '2'],
   ['7782', '166', '427', ' 161', ' 479', ' 204', '2'],
   ['7783', '166', '428', ' 162', ' 480', ' 205', '2'],
   ['7784', '166', '429', ' 163', ' 482', ' 207', '2'],
   ['7785', '166', '430', ' 165', ' 483', ' 209', '2'],
   ['7786', '166', '432', ' 166', ' 485', ' 211', '2'],
   ['7787', '166', '432', ' 167', ' 486', ' 213', '2'],
   ['7788', '166', '433', ' 168', ' 488', ' 215', '2'],
   ['7789', '166', '434', ' 169', ' 490', ' 216', '2'],
   ['7790', '166', '435', ' 170', ' 491', ' 217', '2'],
   ['7791', '166', '435', ' 171', ' 493', ' 220', '2'],
   ['7792', '166', '436', ' 173', ' 496', ' 224', '2'],
   ['7793', '166', '437', ' 174', ' 498', ' 226', '2'],
   ['7794', '166', '439', ' 177', ' 498', ' 228', '2'],
   ['7795', '166', '441', ' 179', ' 499', ' 228', '2'],
   ['7796', '166', '442', ' 181', ' 501', ' 230', '2'],
   ['7797', '166', '444', ' 183', ' 505', ' 234', '2'],
   ['7798', '166', '446', ' 184', ' 509', ' 237', '2'],
   ['7799', '166', '446', ' 186', ' 509', ' 239', '2'],
   ['7800', '166', '447', ' 187', ' 511', ' 241', '2'],
   ['7801', '166', '448', ' 190', ' 513', ' 243', '2'],
   ['7802', '166', '449', ' 192', ' 518', ' 249', '2'],
   ['7803', '166', '451', ' 192', ' 523', ' 251', '2'],
   ['7804', '166', '453', ' 194', ' 525', ' 254', '2'],
   ['7805', '166', '455', ' 197', ' 526', ' 256', '2'],
   ['7806', '166', '457', ' 198', ' 530', ' 259', '2'],
   ['7807', '166', '458', ' 200', ' 533', ' 262', '2'],
   ['7808', '166', '459', ' 202', ' 535', ' 265', '2'],
   ['7809', '166', '461', ' 204', ' 537', ' 267', '2'],
   ['7810', '166', '462', ' 206', ' 541', ' 270', '2'],
   ['7811', '166', '466', ' 209', ' 546', ' 275', '2'],
   ['7812', '166', '469', ' 212', ' 549', ' 277', '2'],
   ['7813', '166', '470', ' 215', ' 553', ' 282', '2'],
   ['7814', '166', '472', ' 218', ' 558', ' 288', '2'],
   ['7815', '166', '474', ' 219', ' 562', ' 291', '2'],
   ['7816', '166', '476', ' 222', ' 566', ' 295', '2'],
   ['7817', '166', '478', ' 224', ' 572', ' 300', '2'],
   ['7818', '166', '481', ' 229', ' 575', ' 304', '2'],
   ['7819', '166', '485', ' 231', ' 581', ' 308', '2'],
   ['7820', '166', '487', ' 235', ' 587', ' 315', '2'],
   ['7821', '166', '491', ' 239', ' 593', ' 321', '2'],
   ['7822', '166', '494', ' 243', ' 599', ' 327', '2'],
   ['7823', '166', '498', ' 248', ' 604', ' 332', '2'],
   ['7824', '166', '502', ' 251', ' 611', ' 338', '2'],
   ['7825', '166', '504', ' 254', ' 618', ' 345', '2'],
   ['7826', '166', '510', ' 259', ' 625', ' 352', '2'],
   ['7827', '166', '513', ' 263', ' 633', ' 359', '2'],
   ['7828', '166', '517', ' 269', ' 642', ' 368', '2'],
   ['7829', '166', '522', ' 274', ' 651', ' 376', '2'],
   ['7830', '166', '526', ' 278', ' 660', ' 386', '2'],
   ['7831', '166', '529', ' 284', ' 669', ' 397', '2'],
   ['7832', '166', '534', ' 290', ' 679', ' 407', '2'],
   ['7833', '166', '543', ' 296', ' 687', ' 411', '2'],
   ['7834', '166', '552', ' 302', ' 695', ' 414', '2'],
   ['7835', '166', '564', ' 310', ' 701', ' 416', '2'],
   ['7836', '166', '572', ' 317', ' 711', ' 421', '2'],
   ['7837', '166', '582', ' 323', ' 714', ' 419', '2'],
   ['7838', '166', '594', ' 328', ' 718', ' 414', '2'],
   ['7839', '166', '608', ' 339', ' 721', ' 413', '2'],
   ['7840', '166', '616', ' 347', ' 724', ' 413', '2'],
   ['7841', '166', '630', ' 357', ' 728', ' 413', '2']]},
 {'185': [['8698', '185', '337', ' 124', ' 377', ' 149', '2'],
   ['8699', '185', '336', ' 125', ' 378', ' 151', '2'],
   ['8700', '185', '336', ' 126', ' 378', ' 153', '2'],
   ['8702', '185', '336', ' 127', ' 378', ' 154', '2'],
   ['8707', '185', '335', ' 128', ' 378', ' 156', '2'],
   ['8708', '185', '336', ' 129', ' 379', ' 158', '2'],
   ['8709', '185', '336', ' 130', ' 379', ' 159', '2'],
   ['8712', '185', '336', ' 131', ' 379', ' 160', '2'],
   ['8713', '185', '336', ' 131', ' 381', ' 162', '2'],
   ['8714', '185', '338', ' 131', ' 386', ' 164', '2'],
   ['8715', '185', '337', ' 131', ' 384', ' 165', '2'],
   ['8716', '185', '336', ' 132', ' 383', ' 166', '2'],
   ['8717', '185', '336', ' 133', ' 382', ' 167', '2'],
   ['8718', '185', '339', ' 134', ' 387', ' 170', '2'],
   ['8719', '185', '337', ' 135', ' 386', ' 172', '2'],
   ['8721', '185', '337', ' 136', ' 385', ' 173', '2'],
   ['8722', '185', '337', ' 136', ' 385', ' 174', '2'],
   ['8723', '185', '337', ' 135', ' 387', ' 175', '2'],
   ['8724', '185', '337', ' 136', ' 387', ' 176', '2'],
   ['8725', '185', '338', ' 138', ' 385', ' 177', '2'],
   ['8726', '185', '337', ' 139', ' 385', ' 179', '2'],
   ['8727', '185', '337', ' 141', ' 384', ' 180', '2'],
   ['8728', '185', '338', ' 141', ' 384', ' 180', '2'],
   ['8729', '185', '338', ' 141', ' 385', ' 182', '2'],
   ['8730', '185', '339', ' 143', ' 384', ' 183', '2'],
   ['8731', '185', '340', ' 145', ' 385', ' 185', '2'],
   ['8732', '185', '340', ' 145', ' 386', ' 186', '2'],
   ['8733', '185', '340', ' 145', ' 386', ' 186', '2'],
   ['8734', '185', '341', ' 146', ' 386', ' 187', '2'],
   ['8735', '185', '341', ' 147', ' 386', ' 188', '2'],
   ['8736', '185', '341', ' 147', ' 386', ' 190', '2'],
   ['8737', '185', '340', ' 147', ' 388', ' 192', '2'],
   ['8738', '185', '340', ' 149', ' 387', ' 195', '2'],
   ['8739', '185', '341', ' 153', ' 387', ' 197', '2'],
   ['8740', '185', '341', ' 153', ' 388', ' 199', '2'],
   ['8741', '185', '341', ' 154', ' 389', ' 201', '2'],
   ['8742', '185', '341', ' 155', ' 389', ' 202', '2'],
   ['8743', '185', '343', ' 158', ' 389', ' 203', '2'],
   ['8744', '185', '342', ' 157', ' 391', ' 206', '2'],
   ['8745', '185', '342', ' 158', ' 392', ' 209', '2'],
   ['8746', '185', '342', ' 158', ' 393', ' 211', '2'],
   ['8747', '185', '342', ' 160', ' 393', ' 213', '2'],
   ['8748', '185', '343', ' 162', ' 393', ' 215', '2'],
   ['8749', '185', '343', ' 163', ' 393', ' 217', '2'],
   ['8750', '185', '342', ' 164', ' 394', ' 219', '2'],
   ['8751', '185', '342', ' 165', ' 395', ' 222', '2'],
   ['8752', '185', '341', ' 165', ' 396', ' 225', '2'],
   ['8753', '185', '341', ' 166', ' 397', ' 227', '2'],
   ['8754', '185', '341', ' 167', ' 398', ' 229', '2'],
   ['8755', '185', '341', ' 168', ' 398', ' 232', '2'],
   ['8756', '185', '342', ' 171', ' 399', ' 234', '2'],
   ['8757', '185', '342', ' 173', ' 400', ' 238', '2'],
   ['8758', '185', '343', ' 175', ' 402', ' 240', '2'],
   ['8759', '185', '343', ' 177', ' 404', ' 245', '2'],
   ['8760', '185', '342', ' 178', ' 406', ' 249', '2'],
   ['8761', '185', '343', ' 182', ' 407', ' 252', '2'],
   ['8762', '185', '343', ' 184', ' 409', ' 257', '2'],
   ['8763', '185', '342', ' 185', ' 411', ' 261', '2'],
   ['8764', '185', '343', ' 190', ' 411', ' 264', '2'],
   ['8765', '185', '341', ' 190', ' 412', ' 269', '2'],
   ['8766', '185', '342', ' 195', ' 413', ' 274', '2'],
   ['8767', '185', '341', ' 196', ' 415', ' 277', '2'],
   ['8768', '185', '342', ' 198', ' 417', ' 281', '2'],
   ['8769', '185', '342', ' 201', ' 418', ' 284', '2'],
   ['8770', '185', '342', ' 203', ' 421', ' 290', '2'],
   ['8771', '185', '342', ' 206', ' 425', ' 297', '2'],
   ['8772', '185', '342', ' 208', ' 426', ' 300', '2'],
   ['8773', '185', '342', ' 213', ' 427', ' 307', '2'],
   ['8774', '185', '342', ' 216', ' 429', ' 312', '2'],
   ['8775', '185', '343', ' 219', ' 433', ' 319', '2'],
   ['8776', '185', '344', ' 223', ' 436', ' 324', '2'],
   ['8777', '185', '343', ' 226', ' 438', ' 330', '2'],
   ['8778', '185', '344', ' 229', ' 442', ' 337', '2'],
   ['8779', '185', '343', ' 233', ' 445', ' 347', '2'],
   ['8780', '185', '344', ' 239', ' 447', ' 354', '2'],
   ['8781', '185', '343', ' 242', ' 450', ' 361', '2'],
   ['8782', '185', '343', ' 247', ' 454', ' 371', '2'],
   ['8786', '185', '344', ' 262', ' 466', ' 398', '2'],
   ['8787', '185', '346', ' 271', ' 471', ' 409', '2'],
   ['8788', '185', '350', ' 280', ' 473', ' 415', '2'],
   ['8789', '185', '356', ' 287', ' 475', ' 415', '2'],
   ['8794', '185', '373', ' 315', ' 470', ' 414', '2'],
   ['8795', '185', '383', ' 336', ' 467', ' 415', '2']]},
 {'190': [['8924', '190', '368', ' 107', ' 391', ' 120', '2'],
   ['8925', '190', '368', ' 108', ' 391', ' 121', '2'],
   ['8932', '190', '368', ' 108', ' 393', ' 121', '2'],
   ['8939', '190', '370', ' 110', ' 396', ' 124', '2'],
   ['8940', '190', '371', ' 110', ' 396', ' 125', '2'],
   ['8941', '190', '371', ' 111', ' 398', ' 126', '2'],
   ['8942', '190', '371', ' 110', ' 399', ' 126', '2'],
   ['8943', '190', '371', ' 110', ' 399', ' 126', '2'],
   ['8944', '190', '370', ' 109', ' 399', ' 126', '2'],
   ['8945', '190', '370', ' 109', ' 400', ' 126', '2'],
   ['8946', '190', '371', ' 109', ' 400', ' 126', '2'],
   ['8947', '190', '372', ' 109', ' 401', ' 127', '2'],
   ['8948', '190', '372', ' 110', ' 401', ' 127', '2'],
   ['8949', '190', '373', ' 110', ' 401', ' 127', '2'],
   ['8950', '190', '373', ' 110', ' 401', ' 127', '2'],
   ['8951', '190', '374', ' 110', ' 401', ' 127', '2'],
   ['8952', '190', '374', ' 110', ' 401', ' 127', '2'],
   ['8953', '190', '374', ' 110', ' 401', ' 127', '2'],
   ['8954', '190', '374', ' 110', ' 401', ' 127', '2'],
   ['8955', '190', '374', ' 110', ' 402', ' 127', '2'],
   ['8956', '190', '374', ' 110', ' 402', ' 128', '2'],
   ['8957', '190', '374', ' 110', ' 402', ' 128', '2'],
   ['8958', '190', '374', ' 110', ' 403', ' 129', '2'],
   ['8959', '190', '375', ' 110', ' 403', ' 129', '2'],
   ['8960', '190', '377', ' 113', ' 402', ' 130', '2'],
   ['8961', '190', '377', ' 113', ' 403', ' 131', '2'],
   ['8962', '190', '377', ' 112', ' 405', ' 131', '2'],
   ['8963', '190', '377', ' 113', ' 405', ' 132', '2'],
   ['8964', '190', '378', ' 113', ' 406', ' 132', '2'],
   ['8965', '190', '378', ' 113', ' 405', ' 132', '2'],
   ['8966', '190', '378', ' 113', ' 405', ' 132', '2'],
   ['8967', '190', '379', ' 115', ' 405', ' 133', '2'],
   ['8968', '190', '379', ' 115', ' 406', ' 133', '2'],
   ['8969', '190', '379', ' 114', ' 406', ' 133', '2'],
   ['8970', '190', '379', ' 114', ' 407', ' 133', '2'],
   ['8971', '190', '379', ' 114', ' 407', ' 133', '2'],
   ['8972', '190', '380', ' 115', ' 406', ' 134', '2'],
   ['8973', '190', '380', ' 115', ' 408', ' 134', '2'],
   ['8974', '190', '380', ' 114', ' 408', ' 134', '2'],
   ['8975', '190', '380', ' 114', ' 408', ' 135', '2'],
   ['8976', '190', '381', ' 114', ' 409', ' 134', '2'],
   ['8977', '190', '381', ' 114', ' 409', ' 134', '2'],
   ['8978', '190', '381', ' 113', ' 410', ' 134', '2'],
   ['8979', '190', '381', ' 113', ' 410', ' 135', '2'],
   ['8980', '190', '380', ' 114', ' 410', ' 136', '2'],
   ['8981', '190', '381', ' 115', ' 410', ' 136', '2'],
   ['8982', '190', '382', ' 116', ' 410', ' 137', '2'],
   ['8983', '190', '382', ' 116', ' 411', ' 137', '2'],
   ['8984', '190', '383', ' 116', ' 411', ' 138', '2'],
   ['8985', '190', '384', ' 117', ' 412', ' 138', '2'],
   ['8986', '190', '384', ' 117', ' 412', ' 138', '2'],
   ['8987', '190', '385', ' 118', ' 413', ' 139', '2'],
   ['8988', '190', '385', ' 118', ' 414', ' 139', '2'],
   ['8989', '190', '385', ' 117', ' 415', ' 139', '2'],
   ['8990', '190', '386', ' 119', ' 415', ' 140', '2'],
   ['8991', '190', '387', ' 118', ' 416', ' 140', '2'],
   ['8992', '190', '388', ' 119', ' 417', ' 141', '2'],
   ['8993', '190', '388', ' 119', ' 416', ' 141', '2'],
   ['8994', '190', '389', ' 120', ' 417', ' 141', '2'],
   ['8995', '190', '389', ' 121', ' 417', ' 142', '2'],
   ['8996', '190', '389', ' 121', ' 418', ' 143', '2'],
   ['8997', '190', '389', ' 122', ' 419', ' 144', '2'],
   ['8998', '190', '389', ' 122', ' 419', ' 145', '2'],
   ['8999', '190', '389', ' 122', ' 420', ' 145', '2'],
   ['9000', '190', '390', ' 123', ' 420', ' 146', '2'],
   ['9001', '190', '390', ' 122', ' 422', ' 146', '2'],
   ['9002', '190', '390', ' 122', ' 422', ' 147', '2'],
   ['9003', '190', '390', ' 122', ' 423', ' 147', '2'],
   ['9004', '190', '392', ' 123', ' 423', ' 147', '2'],
   ['9005', '190', '393', ' 124', ' 423', ' 147', '2'],
   ['9006', '190', '393', ' 125', ' 423', ' 148', '2'],
   ['9007', '190', '394', ' 126', ' 424', ' 148', '2'],
   ['9008', '190', '394', ' 127', ' 425', ' 149', '2'],
   ['9009', '190', '395', ' 127', ' 426', ' 150', '2'],
   ['9010', '190', '395', ' 127', ' 427', ' 150', '2'],
   ['9011', '190', '395', ' 127', ' 428', ' 151', '2'],
   ['9012', '190', '395', ' 128', ' 428', ' 152', '2'],
   ['9013', '190', '396', ' 129', ' 427', ' 152', '2'],
   ['9014', '190', '397', ' 130', ' 428', ' 152', '2'],
   ['9015', '190', '397', ' 130', ' 429', ' 153', '2'],
   ['9016', '190', '397', ' 130', ' 430', ' 154', '2'],
   ['9017', '190', '398', ' 130', ' 432', ' 155', '2'],
   ['9018', '190', '398', ' 130', ' 433', ' 155', '2'],
   ['9019', '190', '398', ' 130', ' 435', ' 157', '2'],
   ['9020', '190', '398', ' 131', ' 435', ' 157', '2'],
   ['9021', '190', '399', ' 131', ' 435', ' 158', '2'],
   ['9022', '190', '399', ' 132', ' 436', ' 158', '2'],
   ['9023', '190', '400', ' 132', ' 436', ' 158', '2'],
   ['9024', '190', '400', ' 132', ' 437', ' 159', '2'],
   ['9025', '190', '401', ' 133', ' 437', ' 159', '2'],
   ['9026', '190', '401', ' 134', ' 437', ' 160', '2'],
   ['9027', '190', '401', ' 133', ' 439', ' 160', '2'],
   ['9028', '190', '403', ' 134', ' 440', ' 161', '2'],
   ['9029', '190', '403', ' 134', ' 442', ' 162', '2'],
   ['9030', '190', '404', ' 135', ' 444', ' 163', '2'],
   ['9031', '190', '404', ' 135', ' 445', ' 164', '2'],
   ['9032', '190', '404', ' 136', ' 444', ' 165', '2'],
   ['9033', '190', '406', ' 137', ' 446', ' 165', '2'],
   ['9034', '190', '406', ' 138', ' 446', ' 166', '2'],
   ['9035', '190', '406', ' 138', ' 447', ' 167', '2'],
   ['9036', '190', '407', ' 139', ' 449', ' 168', '2'],
   ['9037', '190', '408', ' 139', ' 450', ' 169', '2'],
   ['9038', '190', '408', ' 140', ' 450', ' 170', '2'],
   ['9039', '190', '409', ' 141', ' 451', ' 171', '2'],
   ['9040', '190', '409', ' 141', ' 452', ' 172', '2'],
   ['9041', '190', '410', ' 141', ' 451', ' 172', '2'],
   ['9042', '190', '411', ' 142', ' 452', ' 172', '2'],
   ['9043', '190', '412', ' 143', ' 453', ' 173', '2'],
   ['9044', '190', '412', ' 144', ' 454', ' 174', '2'],
   ['9045', '190', '413', ' 144', ' 456', ' 175', '2'],
   ['9046', '190', '415', ' 145', ' 458', ' 177', '2'],
   ['9047', '190', '415', ' 146', ' 459', ' 178', '2'],
   ['9048', '190', '416', ' 146', ' 460', ' 179', '2'],
   ['9049', '190', '416', ' 146', ' 461', ' 180', '2'],
   ['9050', '190', '416', ' 147', ' 462', ' 181', '2'],
   ['9051', '190', '417', ' 148', ' 463', ' 183', '2'],
   ['9052', '190', '418', ' 149', ' 464', ' 184', '2'],
   ['9053', '190', '418', ' 149', ' 465', ' 184', '2'],
   ['9054', '190', '419', ' 149', ' 466', ' 185', '2'],
   ['9055', '190', '421', ' 152', ' 465', ' 185', '2'],
   ['9056', '190', '420', ' 152', ' 466', ' 187', '2'],
   ['9057', '190', '420', ' 152', ' 468', ' 189', '2'],
   ['9058', '190', '422', ' 153', ' 469', ' 190', '2'],
   ['9059', '190', '424', ' 156', ' 469', ' 191', '2'],
   ['9060', '190', '423', ' 156', ' 470', ' 192', '2'],
   ['9061', '190', '424', ' 157', ' 472', ' 195', '2'],
   ['9062', '190', '425', ' 157', ' 474', ' 196', '2'],
   ['9063', '190', '427', ' 159', ' 475', ' 197', '2'],
   ['9064', '190', '427', ' 159', ' 478', ' 199', '2'],
   ['9065', '190', '427', ' 159', ' 479', ' 200', '2'],
   ['9066', '190', '429', ' 160', ' 481', ' 202', '2'],
   ['9067', '190', '429', ' 161', ' 479', ' 201', '2'],
   ['9068', '190', '429', ' 163', ' 481', ' 204', '2'],
   ['9069', '190', '431', ' 164', ' 483', ' 205', '2'],
   ['9070', '190', '431', ' 165', ' 484', ' 207', '2'],
   ['9071', '190', '430', ' 165', ' 485', ' 209', '2'],
   ['9072', '190', '432', ' 166', ' 487', ' 210', '2'],
   ['9073', '190', '431', ' 166', ' 488', ' 211', '2'],
   ['9074', '190', '433', ' 167', ' 490', ' 213', '2'],
   ['9075', '190', '433', ' 168', ' 491', ' 215', '2'],
   ['9076', '190', '434', ' 169', ' 493', ' 217', '2'],
   ['9077', '190', '435', ' 170', ' 493', ' 218', '2'],
   ['9078', '190', '435', ' 172', ' 495', ' 221', '2'],
   ['9079', '190', '437', ' 173', ' 497', ' 223', '2'],
   ['9080', '190', '439', ' 175', ' 498', ' 225', '2'],
   ['9081', '190', '440', ' 177', ' 499', ' 226', '2'],
   ['9082', '190', '442', ' 178', ' 501', ' 227', '2'],
   ['9083', '190', '443', ' 179', ' 503', ' 229', '2'],
   ['9084', '190', '442', ' 180', ' 506', ' 233', '2'],
   ['9085', '190', '444', ' 183', ' 507', ' 236', '2'],
   ['9086', '190', '445', ' 185', ' 508', ' 238', '2'],
   ['9087', '190', '445', ' 186', ' 510', ' 240', '2'],
   ['9088', '190', '448', ' 189', ' 512', ' 242', '2'],
   ['9089', '190', '449', ' 190', ' 514', ' 245', '2'],
   ['9090', '190', '451', ' 192', ' 517', ' 247', '2'],
   ['9091', '190', '452', ' 194', ' 519', ' 250', '2'],
   ['9092', '190', '452', ' 196', ' 521', ' 253', '2'],
   ['9093', '190', '453', ' 197', ' 524', ' 256', '2'],
   ['9094', '190', '454', ' 198', ' 527', ' 258', '2'],
   ['9095', '190', '455', ' 199', ' 529', ' 261', '2'],
   ['9096', '190', '457', ' 200', ' 531', ' 262', '2'],
   ['9097', '190', '458', ' 202', ' 533', ' 266', '2'],
   ['9098', '190', '458', ' 203', ' 538', ' 271', '2'],
   ['9099', '190', '459', ' 204', ' 541', ' 274', '2'],
   ['9100', '190', '462', ' 208', ' 543', ' 277', '2'],
   ['9101', '190', '464', ' 211', ' 545', ' 280', '2'],
   ['9102', '190', '465', ' 214', ' 548', ' 285', '2'],
   ['9103', '190', '468', ' 216', ' 552', ' 288', '2'],
   ['9104', '190', '469', ' 218', ' 556', ' 293', '2'],
   ['9105', '190', '470', ' 221', ' 558', ' 297', '2'],
   ['9106', '190', '473', ' 224', ' 561', ' 300', '2'],
   ['9107', '190', '474', ' 225', ' 565', ' 304', '2'],
   ['9108', '190', '476', ' 229', ' 569', ' 310', '2'],
   ['9109', '190', '479', ' 232', ' 573', ' 313', '2'],
   ['9110', '190', '481', ' 235', ' 577', ' 319', '2'],
   ['9111', '190', '484', ' 239', ' 582', ' 325', '2'],
   ['9112', '190', '487', ' 242', ' 587', ' 329', '2'],
   ['9113', '190', '489', ' 245', ' 591', ' 335', '2'],
   ['9114', '190', '490', ' 248', ' 596', ' 340', '2'],
   ['9115', '190', '493', ' 251', ' 601', ' 346', '2'],
   ['9116', '190', '496', ' 256', ' 605', ' 351', '2'],
   ['9117', '190', '499', ' 260', ' 610', ' 358', '2'],
   ['9118', '190', '502', ' 265', ' 615', ' 365', '2'],
   ['9119', '190', '505', ' 269', ' 622', ' 372', '2'],
   ['9120', '190', '508', ' 273', ' 629', ' 380', '2'],
   ['9121', '190', '511', ' 277', ' 636', ' 388', '2'],
   ['9122', '190', '514', ' 281', ' 645', ' 398', '2'],
   ['9123', '190', '518', ' 287', ' 651', ' 407', '2'],
   ['9124', '190', '523', ' 292', ' 656', ' 411', '2'],
   ['9125', '190', '530', ' 298', ' 660', ' 414', '2'],
   ['9126', '190', '538', ' 304', ' 663', ' 414', '2'],
   ['9127', '190', '548', ' 310', ' 671', ' 416', '2'],
   ['9128', '190', '554', ' 317', ' 673', ' 415', '2'],
   ['9129', '190', '560', ' 322', ' 672', ' 413', '2'],
   ['9130', '190', '567', ' 325', ' 678', ' 412', '2'],
   ['9131', '190', '577', ' 336', ' 681', ' 413', '2'],
   ['9132', '190', '591', ' 344', ' 691', ' 413', '2'],
   ['9133', '190', '600', ' 353', ' 694', ' 412', '2']]},
 {'242': [['10400', '242', '364', ' 106', ' 387', ' 120', '2'],
   ['10401', '242', '364', ' 106', ' 387', ' 120', '2'],
   ['10402', '242', '364', ' 106', ' 386', ' 120', '2'],
   ['10403', '242', '364', ' 106', ' 386', ' 120', '2'],
   ['10404', '242', '364', ' 106', ' 386', ' 120', '2'],
   ['10405', '242', '365', ' 106', ' 387', ' 120', '2'],
   ['10406', '242', '365', ' 107', ' 387', ' 121', '2'],
   ['10407', '242', '365', ' 107', ' 387', ' 121', '2'],
   ['10414', '242', '364', ' 107', ' 389', ' 122', '2'],
   ['10415', '242', '364', ' 107', ' 390', ' 123', '2'],
   ['10416', '242', '364', ' 107', ' 391', ' 123', '2'],
   ['10417', '242', '364', ' 107', ' 391', ' 124', '2'],
   ['10418', '242', '364', ' 107', ' 391', ' 125', '2'],
   ['10419', '242', '364', ' 107', ' 391', ' 125', '2'],
   ['10420', '242', '363', ' 107', ' 391', ' 125', '2'],
   ['10421', '242', '363', ' 107', ' 392', ' 126', '2'],
   ['10422', '242', '364', ' 107', ' 391', ' 126', '2'],
   ['10423', '242', '365', ' 108', ' 392', ' 126', '2'],
   ['10424', '242', '365', ' 108', ' 392', ' 127', '2'],
   ['10425', '242', '365', ' 109', ' 391', ' 127', '2'],
   ['10426', '242', '364', ' 109', ' 391', ' 127', '2'],
   ['10427', '242', '365', ' 109', ' 391', ' 127', '2'],
   ['10428', '242', '364', ' 109', ' 391', ' 127', '2'],
   ['10429', '242', '364', ' 109', ' 391', ' 127', '2'],
   ['10430', '242', '363', ' 109', ' 391', ' 128', '2'],
   ['10431', '242', '363', ' 109', ' 392', ' 129', '2'],
   ['10432', '242', '364', ' 110', ' 392', ' 129', '2'],
   ['10433', '242', '364', ' 112', ' 391', ' 130', '2'],
   ['10434', '242', '365', ' 112', ' 391', ' 131', '2'],
   ['10435', '242', '364', ' 112', ' 392', ' 131', '2'],
   ['10436', '242', '364', ' 112', ' 393', ' 131', '2'],
   ['10437', '242', '364', ' 113', ' 392', ' 132', '2'],
   ['10438', '242', '365', ' 115', ' 391', ' 132', '2'],
   ['10439', '242', '366', ' 117', ' 391', ' 133', '2'],
   ['10440', '242', '366', ' 118', ' 390', ' 134', '2'],
   ['10441', '242', '365', ' 117', ' 391', ' 134', '2'],
   ['10442', '242', '365', ' 117', ' 391', ' 134', '2'],
   ['10443', '242', '365', ' 116', ' 392', ' 134', '2'],
   ['10444', '242', '366', ' 118', ' 391', ' 134', '2'],
   ['10445', '242', '365', ' 118', ' 392', ' 135', '2'],
   ['10446', '242', '366', ' 118', ' 392', ' 135', '2'],
   ['10447', '242', '365', ' 118', ' 393', ' 135', '2'],
   ['10448', '242', '365', ' 118', ' 393', ' 136', '2'],
   ['10449', '242', '364', ' 117', ' 394', ' 137', '2'],
   ['10450', '242', '364', ' 117', ' 394', ' 137', '2'],
   ['10451', '242', '364', ' 117', ' 397', ' 139', '2'],
   ['10452', '242', '366', ' 119', ' 396', ' 139', '2'],
   ['10453', '242', '366', ' 120', ' 395', ' 140', '2'],
   ['10454', '242', '365', ' 119', ' 396', ' 140', '2'],
   ['10455', '242', '363', ' 118', ' 397', ' 141', '2'],
   ['10456', '242', '361', ' 114', ' 400', ' 142', '2'],
   ['10457', '242', '359', ' 112', ' 401', ' 143', '2'],
   ['10458', '242', '360', ' 113', ' 401', ' 143', '2'],
   ['10459', '242', '361', ' 115', ' 400', ' 144', '2'],
   ['10460', '242', '361', ' 115', ' 399', ' 145', '2'],
   ['10461', '242', '361', ' 115', ' 399', ' 145', '2'],
   ['10462', '242', '361', ' 116', ' 399', ' 146', '2'],
   ['10463', '242', '362', ' 116', ' 400', ' 146', '2'],
   ['10464', '242', '363', ' 117', ' 399', ' 147', '2'],
   ['10465', '242', '364', ' 119', ' 398', ' 147', '2'],
   ['10466', '242', '366', ' 121', ' 398', ' 148', '2'],
   ['10467', '242', '365', ' 121', ' 399', ' 150', '2'],
   ['10468', '242', '364', ' 121', ' 399', ' 150', '2'],
   ['10469', '242', '365', ' 122', ' 399', ' 151', '2'],
   ['10470', '242', '366', ' 125', ' 398', ' 152', '2'],
   ['10471', '242', '366', ' 126', ' 397', ' 152', '2'],
   ['10472', '242', '366', ' 126', ' 397', ' 152', '2'],
   ['10473', '242', '366', ' 127', ' 398', ' 153', '2'],
   ['10474', '242', '366', ' 127', ' 399', ' 154', '2'],
   ['10475', '242', '366', ' 127', ' 399', ' 154', '2'],
   ['10477', '242', '365', ' 127', ' 401', ' 157', '2'],
   ['10478', '242', '366', ' 129', ' 400', ' 157', '2'],
   ['10480', '242', '365', ' 129', ' 402', ' 160', '2'],
   ['10481', '242', '366', ' 129', ' 403', ' 161', '2'],
   ['10482', '242', '365', ' 130', ' 403', ' 163', '2'],
   ['10483', '242', '365', ' 130', ' 404', ' 164', '2'],
   ['10484', '242', '365', ' 131', ' 405', ' 165', '2'],
   ['10485', '242', '365', ' 132', ' 405', ' 167', '2'],
   ['10486', '242', '366', ' 133', ' 406', ' 169', '2'],
   ['10487', '242', '366', ' 134', ' 406', ' 170', '2'],
   ['10488', '242', '366', ' 135', ' 406', ' 171', '2'],
   ['10489', '242', '366', ' 136', ' 406', ' 172', '2'],
   ['10490', '242', '367', ' 136', ' 407', ' 173', '2'],
   ['10491', '242', '366', ' 136', ' 408', ' 174', '2'],
   ['10492', '242', '367', ' 136', ' 409', ' 176', '2'],
   ['10493', '242', '367', ' 137', ' 410', ' 177', '2'],
   ['10494', '242', '367', ' 138', ' 411', ' 179', '2'],
   ['10495', '242', '367', ' 140', ' 410', ' 180', '2'],
   ['10496', '242', '367', ' 140', ' 410', ' 182', '2'],
   ['10497', '242', '367', ' 142', ' 411', ' 184', '2'],
   ['10498', '242', '368', ' 142', ' 411', ' 184', '2'],
   ['10499', '242', '368', ' 143', ' 411', ' 185', '2'],
   ['10500', '242', '368', ' 144', ' 413', ' 187', '2'],
   ['10501', '242', '369', ' 147', ' 414', ' 190', '2'],
   ['10502', '242', '370', ' 148', ' 414', ' 191', '2'],
   ['10503', '242', '370', ' 149', ' 416', ' 193', '2'],
   ['10504', '242', '370', ' 149', ' 417', ' 195', '2'],
   ['10505', '242', '370', ' 150', ' 418', ' 197', '2'],
   ['10506', '242', '370', ' 151', ' 419', ' 199', '2'],
   ['10507', '242', '371', ' 154', ' 420', ' 202', '2'],
   ['10508', '242', '372', ' 156', ' 421', ' 204', '2'],
   ['10509', '242', '372', ' 158', ' 421', ' 206', '2'],
   ['10510', '242', '373', ' 160', ' 423', ' 208', '2'],
   ['10511', '242', '373', ' 160', ' 424', ' 210', '2'],
   ['10512', '242', '373', ' 162', ' 426', ' 212', '2'],
   ['10513', '242', '373', ' 162', ' 427', ' 215', '2'],
   ['10514', '242', '374', ' 163', ' 429', ' 218', '2'],
   ['10515', '242', '373', ' 164', ' 429', ' 220', '2'],
   ['10516', '242', '373', ' 167', ' 431', ' 224', '2'],
   ['10517', '242', '373', ' 167', ' 432', ' 226', '2'],
   ['10518', '242', '374', ' 168', ' 434', ' 228', '2'],
   ['10519', '242', '375', ' 169', ' 436', ' 231', '2'],
   ['10520', '242', '375', ' 171', ' 438', ' 235', '2'],
   ['10521', '242', '376', ' 172', ' 440', ' 238', '2'],
   ['10522', '242', '376', ' 174', ' 443', ' 243', '2'],
   ['10523', '242', '376', ' 177', ' 444', ' 247', '2'],
   ['10524', '242', '377', ' 179', ' 446', ' 250', '2'],
   ['10525', '242', '378', ' 182', ' 447', ' 253', '2'],
   ['10526', '242', '378', ' 183', ' 448', ' 256', '2'],
   ['10527', '242', '379', ' 186', ' 452', ' 262', '2'],
   ['10528', '242', '379', ' 188', ' 454', ' 266', '2'],
   ['10529', '242', '380', ' 190', ' 456', ' 271', '2'],
   ['10530', '242', '381', ' 193', ' 457', ' 274', '2'],
   ['10531', '242', '381', ' 196', ' 460', ' 281', '2'],
   ['10532', '242', '381', ' 199', ' 463', ' 287', '2'],
   ['10533', '242', '383', ' 203', ' 466', ' 293', '2'],
   ['10534', '242', '384', ' 205', ' 469', ' 297', '2'],
   ['10535', '242', '386', ' 209', ' 472', ' 302', '2'],
   ['10536', '242', '387', ' 213', ' 476', ' 308', '2'],
   ['10537', '242', '388', ' 217', ' 481', ' 317', '2'],
   ['10538', '242', '389', ' 221', ' 485', ' 324', '2'],
   ['10539', '242', '390', ' 224', ' 489', ' 331', '2'],
   ['10540', '242', '392', ' 228', ' 493', ' 337', '2'],
   ['10541', '242', '393', ' 232', ' 499', ' 346', '2'],
   ['10542', '242', '395', ' 238', ' 502', ' 353', '2'],
   ['10543', '242', '396', ' 242', ' 509', ' 362', '2'],
   ['10544', '242', '397', ' 246', ' 514', ' 373', '2'],
   ['10545', '242', '398', ' 250', ' 521', ' 383', '2'],
   ['10546', '242', '397', ' 256', ' 530', ' 400', '2'],
   ['10547', '242', '401', ' 263', ' 536', ' 409', '2'],
   ['10548', '242', '406', ' 269', ' 540', ' 413', '2'],
   ['10549', '242', '412', ' 275', ' 543', ' 415', '2'],
   ['10550', '242', '417', ' 281', ' 548', ' 417', '2'],
   ['10551', '242', '427', ' 290', ' 539', ' 402', '2'],
   ['10552', '242', '434', ' 298', ' 545', ' 405', '2'],
   ['10553', '242', '438', ' 306', ' 551', ' 412', '2'],
   ['10554', '242', '446', ' 316', ' 557', ' 414', '2'],
   ['10555', '242', '451', ' 324', ' 556', ' 413', '2']]},
 {'256': [['10641', '256', '369', ' 106', ' 391', ' 120', '2'],
   ['10642', '256', '369', ' 106', ' 391', ' 120', '2'],
   ['10644', '256', '369', ' 106', ' 391', ' 120', '2'],
   ['10645', '256', '370', ' 107', ' 392', ' 121', '2'],
   ['10646', '256', '371', ' 108', ' 392', ' 122', '2'],
   ['10647', '256', '371', ' 109', ' 392', ' 122', '2'],
   ['10648', '256', '371', ' 109', ' 392', ' 122', '2'],
   ['10649', '256', '371', ' 108', ' 393', ' 122', '2'],
   ['10650', '256', '371', ' 108', ' 394', ' 122', '2'],
   ['10651', '256', '371', ' 108', ' 395', ' 123', '2'],
   ['10652', '256', '371', ' 109', ' 396', ' 124', '2'],
   ['10653', '256', '372', ' 109', ' 397', ' 125', '2'],
   ['10654', '256', '372', ' 109', ' 397', ' 126', '2'],
   ['10655', '256', '372', ' 110', ' 397', ' 126', '2'],
   ['10656', '256', '372', ' 108', ' 398', ' 126', '2'],
   ['10657', '256', '372', ' 108', ' 400', ' 126', '2'],
   ['10658', '256', '372', ' 108', ' 401', ' 127', '2'],
   ['10659', '256', '372', ' 108', ' 401', ' 127', '2'],
   ['10660', '256', '373', ' 108', ' 401', ' 127', '2'],
   ['10661', '256', '372', ' 108', ' 401', ' 128', '2'],
   ['10662', '256', '373', ' 108', ' 402', ' 129', '2'],
   ['10663', '256', '373', ' 109', ' 402', ' 129', '2'],
   ['10664', '256', '374', ' 110', ' 403', ' 130', '2'],
   ['10665', '256', '375', ' 112', ' 402', ' 131', '2'],
   ['10666', '256', '376', ' 113', ' 402', ' 132', '2'],
   ['10667', '256', '377', ' 115', ' 402', ' 132', '2'],
   ['10668', '256', '379', ' 118', ' 403', ' 133', '2'],
   ['10669', '256', '380', ' 118', ' 403', ' 134', '2'],
   ['10670', '256', '378', ' 117', ' 405', ' 134', '2'],
   ['10671', '256', '378', ' 117', ' 406', ' 135', '2'],
   ['10672', '256', '378', ' 118', ' 406', ' 136', '2'],
   ['10673', '256', '379', ' 118', ' 408', ' 137', '2'],
   ['10674', '256', '379', ' 118', ' 409', ' 138', '2'],
   ['10675', '256', '379', ' 119', ' 409', ' 139', '2'],
   ['10676', '256', '379', ' 119', ' 410', ' 139', '2'],
   ['10677', '256', '380', ' 120', ' 410', ' 140', '2'],
   ['10678', '256', '379', ' 119', ' 412', ' 140', '2'],
   ['10679', '256', '379', ' 118', ' 413', ' 141', '2'],
   ['10680', '256', '380', ' 119', ' 413', ' 141', '2'],
   ['10681', '256', '380', ' 119', ' 413', ' 142', '2'],
   ['10682', '256', '380', ' 120', ' 414', ' 143', '2'],
   ['10683', '256', '380', ' 121', ' 414', ' 144', '2'],
   ['10684', '256', '380', ' 121', ' 414', ' 145', '2'],
   ['10685', '256', '381', ' 122', ' 415', ' 146', '2'],
   ['10686', '256', '384', ' 124', ' 416', ' 147', '2'],
   ['10687', '256', '383', ' 124', ' 417', ' 148', '2'],
   ['10688', '256', '384', ' 125', ' 419', ' 150', '2'],
   ['10689', '256', '384', ' 125', ' 420', ' 151', '2'],
   ['10690', '256', '385', ' 126', ' 421', ' 152', '2'],
   ['10691', '256', '385', ' 127', ' 422', ' 153', '2'],
   ['10692', '256', '385', ' 128', ' 422', ' 154', '2'],
   ['10693', '256', '386', ' 128', ' 424', ' 155', '2'],
   ['10694', '256', '387', ' 129', ' 424', ' 156', '2'],
   ['10695', '256', '387', ' 130', ' 424', ' 156', '2'],
   ['10696', '256', '387', ' 130', ' 425', ' 158', '2'],
   ['10697', '256', '387', ' 130', ' 427', ' 159', '2'],
   ['10698', '256', '388', ' 131', ' 427', ' 160', '2'],
   ['10699', '256', '389', ' 133', ' 428', ' 161', '2'],
   ['10700', '256', '390', ' 133', ' 429', ' 162', '2'],
   ['10701', '256', '392', ' 134', ' 433', ' 165', '2'],
   ['10702', '256', '392', ' 134', ' 435', ' 166', '2'],
   ['10703', '256', '392', ' 134', ' 435', ' 168', '2'],
   ['10704', '256', '392', ' 135', ' 437', ' 169', '2'],
   ['10705', '256', '393', ' 136', ' 438', ' 171', '2'],
   ['10706', '256', '394', ' 137', ' 440', ' 172', '2'],
   ['10707', '256', '395', ' 138', ' 441', ' 174', '2'],
   ['10708', '256', '396', ' 140', ' 441', ' 175', '2'],
   ['10709', '256', '398', ' 141', ' 441', ' 175', '2'],
   ['10710', '256', '398', ' 142', ' 443', ' 177', '2'],
   ['10711', '256', '399', ' 143', ' 445', ' 178', '2'],
   ['10712', '256', '400', ' 145', ' 446', ' 180', '2'],
   ['10713', '256', '401', ' 146', ' 448', ' 182', '2'],
   ['10714', '256', '402', ' 147', ' 449', ' 184', '2'],
   ['10715', '256', '402', ' 146', ' 452', ' 186', '2'],
   ['10716', '256', '403', ' 147', ' 454', ' 188', '2'],
   ['10717', '256', '404', ' 148', ' 456', ' 190', '2'],
   ['10718', '256', '407', ' 150', ' 457', ' 191', '2'],
   ['10719', '256', '409', ' 152', ' 460', ' 194', '2'],
   ['10720', '256', '409', ' 153', ' 462', ' 197', '2'],
   ['10721', '256', '411', ' 155', ' 464', ' 199', '2'],
   ['10722', '256', '412', ' 157', ' 466', ' 201', '2'],
   ['10723', '256', '413', ' 158', ' 467', ' 203', '2'],
   ['10724', '256', '414', ' 160', ' 469', ' 206', '2'],
   ['10725', '256', '415', ' 161', ' 470', ' 207', '2'],
   ['10726', '256', '416', ' 162', ' 473', ' 210', '2'],
   ['10727', '256', '418', ' 163', ' 475', ' 212', '2'],
   ['10728', '256', '419', ' 165', ' 477', ' 214', '2'],
   ['10729', '256', '421', ' 166', ' 481', ' 217', '2'],
   ['10730', '256', '422', ' 168', ' 484', ' 221', '2'],
   ['10731', '256', '423', ' 172', ' 486', ' 225', '2'],
   ['10732', '256', '425', ' 173', ' 487', ' 227', '2'],
   ['10733', '256', '428', ' 176', ' 491', ' 229', '2'],
   ['10734', '256', '429', ' 178', ' 494', ' 233', '2'],
   ['10735', '256', '430', ' 179', ' 498', ' 236', '2'],
   ['10736', '256', '432', ' 181', ' 500', ' 239', '2'],
   ['10737', '256', '433', ' 183', ' 504', ' 244', '2'],
   ['10738', '256', '436', ' 185', ' 507', ' 246', '2'],
   ['10739', '256', '438', ' 189', ' 510', ' 250', '2'],
   ['10740', '256', '439', ' 191', ' 514', ' 255', '2'],
   ['10741', '256', '440', ' 192', ' 520', ' 260', '2'],
   ['10742', '256', '442', ' 194', ' 523', ' 264', '2'],
   ['10743', '256', '443', ' 196', ' 528', ' 270', '2'],
   ['10744', '256', '447', ' 201', ' 532', ' 275', '2'],
   ['10745', '256', '450', ' 203', ' 536', ' 278', '2'],
   ['10746', '256', '452', ' 205', ' 541', ' 284', '2'],
   ['10747', '256', '455', ' 209', ' 546', ' 289', '2'],
   ['10748', '256', '458', ' 213', ' 551', ' 296', '2'],
   ['10749', '256', '462', ' 217', ' 556', ' 301', '2'],
   ['10750', '256', '464', ' 220', ' 562', ' 307', '2'],
   ['10751', '256', '468', ' 224', ' 568', ' 313', '2'],
   ['10752', '256', '471', ' 228', ' 575', ' 320', '2'],
   ['10753', '256', '474', ' 232', ' 581', ' 327', '2'],
   ['10754', '256', '478', ' 236', ' 588', ' 334', '2'],
   ['10755', '256', '482', ' 242', ' 594', ' 342', '2'],
   ['10756', '256', '486', ' 246', ' 602', ' 350', '2'],
   ['10757', '256', '490', ' 250', ' 610', ' 359', '2'],
   ['10758', '256', '494', ' 256', ' 619', ' 368', '2'],
   ['10759', '256', '500', ' 261', ' 628', ' 377', '2'],
   ['10760', '256', '505', ' 268', ' 638', ' 388', '2'],
   ['10761', '256', '509', ' 273', ' 649', ' 401', '2'],
   ['10762', '256', '515', ' 279', ' 658', ' 409', '2'],
   ['10763', '256', '523', ' 285', ' 665', ' 413', '2'],
   ['10764', '256', '536', ' 293', ' 674', ' 415', '2'],
   ['10765', '256', '545', ' 301', ' 680', ' 417', '2'],
   ['10766', '256', '565', ' 310', ' 695', ' 416', '2'],
   ['10767', '256', '569', ' 319', ' 689', ' 414', '2'],
   ['10768', '256', '578', ' 324', ' 698', ' 414', '2'],
   ['10769', '256', '592', ' 336', ' 703', ' 414', '2'],
   ['10770', '256', '601', ' 346', ' 702', ' 412', '2']]},
 {'267': [['11233', '267', '376', ' 106', ' 395', ' 121', '2'],
   ['11237', '267', '376', ' 107', ' 396', ' 121', '2'],
   ['11238', '267', '376', ' 107', ' 396', ' 122', '2'],
   ['11242', '267', '376', ' 106', ' 399', ' 123', '2'],
   ['11243', '267', '376', ' 107', ' 399', ' 124', '2'],
   ['11244', '267', '377', ' 107', ' 400', ' 125', '2'],
   ['11245', '267', '377', ' 108', ' 400', ' 126', '2'],
   ['11246', '267', '379', ' 108', ' 401', ' 126', '2'],
   ['11247', '267', '379', ' 108', ' 401', ' 126', '2'],
   ['11248', '267', '380', ' 109', ' 402', ' 126', '2'],
   ['11249', '267', '380', ' 109', ' 403', ' 127', '2'],
   ['11250', '267', '380', ' 107', ' 406', ' 127', '2'],
   ['11251', '267', '380', ' 107', ' 406', ' 128', '2'],
   ['11252', '267', '381', ' 107', ' 406', ' 127', '2'],
   ['11253', '267', '381', ' 107', ' 407', ' 128', '2'],
   ['11255', '267', '382', ' 108', ' 408', ' 129', '2'],
   ['11256', '267', '383', ' 108', ' 408', ' 129', '2'],
   ['11257', '267', '383', ' 108', ' 408', ' 129', '2'],
   ['11258', '267', '383', ' 109', ' 408', ' 129', '2'],
   ['11259', '267', '383', ' 108', ' 409', ' 129', '2'],
   ['11260', '267', '383', ' 108', ' 410', ' 130', '2'],
   ['11261', '267', '384', ' 109', ' 410', ' 131', '2'],
   ['11262', '267', '385', ' 111', ' 409', ' 131', '2'],
   ['11263', '267', '385', ' 112', ' 409', ' 131', '2'],
   ['11264', '267', '386', ' 112', ' 410', ' 132', '2'],
   ['11265', '267', '386', ' 113', ' 411', ' 132', '2'],
   ['11266', '267', '388', ' 114', ' 411', ' 133', '2'],
   ['11267', '267', '388', ' 115', ' 412', ' 133', '2'],
   ['11268', '267', '388', ' 113', ' 413', ' 134', '2'],
   ['11269', '267', '389', ' 114', ' 414', ' 134', '2'],
   ['11270', '267', '389', ' 114', ' 414', ' 134', '2'],
   ['11271', '267', '390', ' 114', ' 415', ' 134', '2'],
   ['11272', '267', '390', ' 114', ' 416', ' 134', '2'],
   ['11273', '267', '390', ' 114', ' 416', ' 134', '2'],
   ['11274', '267', '391', ' 114', ' 418', ' 135', '2'],
   ['11275', '267', '391', ' 115', ' 418', ' 136', '2'],
   ['11276', '267', '392', ' 115', ' 419', ' 137', '2'],
   ['11277', '267', '392', ' 116', ' 419', ' 138', '2'],
   ['11278', '267', '392', ' 116', ' 420', ' 138', '2'],
   ['11279', '267', '394', ' 118', ' 421', ' 139', '2'],
   ['11280', '267', '394', ' 118', ' 422', ' 140', '2'],
   ['11281', '267', '394', ' 117', ' 422', ' 140', '2'],
   ['11282', '267', '394', ' 117', ' 423', ' 140', '2'],
   ['11283', '267', '395', ' 117', ' 423', ' 140', '2'],
   ['11284', '267', '396', ' 117', ' 422', ' 139', '2'],
   ['11285', '267', '395', ' 118', ' 424', ' 141', '2'],
   ['11286', '267', '395', ' 118', ' 425', ' 142', '2'],
   ['11287', '267', '396', ' 118', ' 426', ' 142', '2'],
   ['11288', '267', '396', ' 117', ' 426', ' 143', '2'],
   ['11289', '267', '396', ' 117', ' 427', ' 143', '2'],
   ['11290', '267', '396', ' 117', ' 428', ' 145', '2'],
   ['11291', '267', '396', ' 117', ' 429', ' 146', '2'],
   ['11292', '267', '397', ' 118', ' 429', ' 146', '2'],
   ['11293', '267', '398', ' 118', ' 430', ' 147', '2'],
   ['11294', '267', '399', ' 119', ' 430', ' 147', '2'],
   ['11295', '267', '400', ' 120', ' 430', ' 147', '2'],
   ['11296', '267', '400', ' 120', ' 431', ' 148', '2'],
   ['11297', '267', '401', ' 120', ' 433', ' 149', '2'],
   ['11298', '267', '402', ' 121', ' 434', ' 150', '2'],
   ['11299', '267', '402', ' 121', ' 434', ' 150', '2'],
   ['11300', '267', '403', ' 122', ' 435', ' 151', '2'],
   ['11301', '267', '403', ' 123', ' 436', ' 152', '2'],
   ['11302', '267', '403', ' 123', ' 436', ' 153', '2'],
   ['11303', '267', '404', ' 123', ' 438', ' 154', '2'],
   ['11304', '267', '405', ' 123', ' 438', ' 154', '2'],
   ['11305', '267', '406', ' 124', ' 439', ' 155', '2'],
   ['11306', '267', '407', ' 126', ' 440', ' 156', '2'],
   ['11307', '267', '407', ' 126', ' 440', ' 156', '2'],
   ['11308', '267', '408', ' 127', ' 442', ' 158', '2'],
   ['11309', '267', '408', ' 127', ' 443', ' 159', '2'],
   ['11310', '267', '408', ' 127', ' 444', ' 160', '2'],
   ['11311', '267', '410', ' 128', ' 445', ' 161', '2'],
   ['11312', '267', '411', ' 129', ' 446', ' 161', '2'],
   ['11313', '267', '411', ' 129', ' 447', ' 162', '2'],
   ['11314', '267', '413', ' 130', ' 448', ' 163', '2'],
   ['11315', '267', '413', ' 131', ' 450', ' 164', '2'],
   ['11316', '267', '413', ' 130', ' 451', ' 165', '2'],
   ['11317', '267', '414', ' 131', ' 451', ' 166', '2'],
   ['11318', '267', '415', ' 131', ' 453', ' 166', '2'],
   ['11319', '267', '416', ' 131', ' 455', ' 168', '2'],
   ['11320', '267', '416', ' 133', ' 455', ' 169', '2'],
   ['11321', '267', '417', ' 133', ' 457', ' 171', '2'],
   ['11322', '267', '417', ' 133', ' 457', ' 172', '2'],
   ['11323', '267', '418', ' 133', ' 458', ' 173', '2'],
   ['11324', '267', '420', ' 134', ' 460', ' 173', '2'],
   ['11325', '267', '421', ' 135', ' 461', ' 174', '2'],
   ['11326', '267', '422', ' 136', ' 462', ' 176', '2'],
   ['11327', '267', '423', ' 136', ' 464', ' 177', '2'],
   ['11328', '267', '424', ' 138', ' 463', ' 177', '2'],
   ['11329', '267', '425', ' 139', ' 464', ' 178', '2'],
   ['11330', '267', '425', ' 139', ' 465', ' 179', '2'],
   ['11331', '267', '425', ' 140', ' 466', ' 181', '2'],
   ['11332', '267', '426', ' 141', ' 467', ' 182', '2'],
   ['11333', '267', '427', ' 142', ' 468', ' 184', '2'],
   ['11334', '267', '427', ' 143', ' 469', ' 185', '2'],
   ['11335', '267', '428', ' 143', ' 471', ' 186', '2'],
   ['11336', '267', '430', ' 144', ' 473', ' 187', '2'],
   ['11337', '267', '430', ' 145', ' 474', ' 189', '2'],
   ['11338', '267', '431', ' 146', ' 475', ' 190', '2'],
   ['11339', '267', '433', ' 147', ' 476', ' 191', '2'],
   ['11340', '267', '433', ' 149', ' 478', ' 193', '2'],
   ['11341', '267', '433', ' 150', ' 479', ' 195', '2'],
   ['11342', '267', '433', ' 150', ' 481', ' 197', '2'],
   ['11343', '267', '434', ' 151', ' 482', ' 198', '2'],
   ['11344', '267', '437', ' 152', ' 485', ' 200', '2'],
   ['11345', '267', '438', ' 153', ' 487', ' 202', '2'],
   ['11346', '267', '439', ' 155', ' 489', ' 204', '2'],
   ['11347', '267', '441', ' 156', ' 490', ' 206', '2'],
   ['11348', '267', '442', ' 157', ' 492', ' 207', '2'],
   ['11349', '267', '443', ' 158', ' 493', ' 208', '2'],
   ['11350', '267', '443', ' 159', ' 495', ' 209', '2'],
   ['11351', '267', '443', ' 159', ' 497', ' 211', '2'],
   ['11352', '267', '445', ' 160', ' 498', ' 213', '2'],
   ['11353', '267', '446', ' 162', ' 501', ' 216', '2'],
   ['11354', '267', '447', ' 163', ' 503', ' 219', '2'],
   ['11355', '267', '448', ' 164', ' 506', ' 220', '2'],
   ['11356', '267', '450', ' 166', ' 508', ' 223', '2'],
   ['11357', '267', '450', ' 167', ' 510', ' 226', '2'],
   ['11358', '267', '451', ' 167', ' 512', ' 228', '2'],
   ['11359', '267', '454', ' 168', ' 516', ' 230', '2'],
   ['11360', '267', '455', ' 169', ' 518', ' 232', '2'],
   ['11361', '267', '459', ' 173', ' 522', ' 236', '2'],
   ['11362', '267', '463', ' 176', ' 525', ' 239', '2'],
   ['11363', '267', '461', ' 176', ' 525', ' 241', '2'],
   ['11364', '267', '462', ' 177', ' 529', ' 245', '2'],
   ['11365', '267', '462', ' 178', ' 533', ' 249', '2'],
   ['11367', '267', '466', ' 182', ' 536', ' 252', '2'],
   ['11368', '267', '473', ' 190', ' 540', ' 257', '2'],
   ['11369', '267', '474', ' 191', ' 544', ' 260', '2'],
   ['11370', '267', '473', ' 188', ' 548', ' 264', '2'],
   ['11371', '267', '474', ' 190', ' 552', ' 267', '2'],
   ['11372', '267', '480', ' 195', ' 557', ' 272', '2'],
   ['11373', '267', '483', ' 202', ' 558', ' 277', '2'],
   ['11374', '267', '484', ' 203', ' 561', ' 279', '2'],
   ['11375', '267', '484', ' 200', ' 568', ' 283', '2'],
   ['11376', '267', '485', ' 201', ' 572', ' 288', '2'],
   ['11377', '267', '487', ' 202', ' 577', ' 293', '2'],
   ['11378', '267', '488', ' 204', ' 582', ' 297', '2'],
   ['11379', '267', '491', ' 206', ' 587', ' 302', '2'],
   ['11380', '267', '494', ' 209', ' 591', ' 306', '2'],
   ['11381', '267', '497', ' 213', ' 595', ' 312', '2'],
   ['11382', '267', '500', ' 217', ' 601', ' 318', '2'],
   ['11383', '267', '503', ' 219', ' 607', ' 324', '2'],
   ['11384', '267', '507', ' 222', ' 613', ' 329', '2'],
   ['11385', '267', '511', ' 224', ' 619', ' 333', '2'],
   ['11386', '267', '514', ' 228', ' 625', ' 341', '2'],
   ['11387', '267', '517', ' 231', ' 633', ' 349', '2'],
   ['11388', '267', '520', ' 235', ' 639', ' 355', '2'],
   ['11389', '267', '526', ' 240', ' 647', ' 363', '2'],
   ['11390', '267', '529', ' 243', ' 654', ' 370', '2'],
   ['11391', '267', '532', ' 247', ' 663', ' 380', '2'],
   ['11392', '267', '537', ' 252', ' 672', ' 389', '2'],
   ['11393', '267', '540', ' 256', ' 682', ' 401', '2'],
   ['11394', '267', '547', ' 262', ' 690', ' 408', '2'],
   ['11395', '267', '555', ' 267', ' 697', ' 411', '2'],
   ['11396', '267', '568', ' 273', ' 712', ' 415', '2'],
   ['11397', '267', '577', ' 277', ' 723', ' 418', '2'],
   ['11398', '267', '582', ' 280', ' 729', ' 419', '2'],
   ['11399', '267', '590', ' 288', ' 730', ' 417', '2'],
   ['11400', '267', '597', ' 296', ' 731', ' 415', '2'],
   ['11401', '267', '606', ' 303', ' 735', ' 414', '2'],
   ['11402', '267', '616', ' 310', ' 741', ' 413', '2'],
   ['11403', '267', '625', ' 318', ' 747', ' 414', '2'],
   ['11404', '267', '635', ' 326', ' 751', ' 414', '2'],
   ['11405', '267', '641', ' 329', ' 757', ' 413', '2']]},
 {'358': [['13898', '358', '363', ' 109', ' 389', ' 132', '2'],
   ['13899', '358', '363', ' 109', ' 390', ' 133', '2'],
   ['13900', '358', '362', ' 109', ' 391', ' 134', '2'],
   ['13901', '358', '364', ' 111', ' 390', ' 135', '2'],
   ['13902', '358', '363', ' 109', ' 392', ' 135', '2'],
   ['13903', '358', '363', ' 109', ' 392', ' 135', '2'],
   ['13904', '358', '363', ' 109', ' 393', ' 135', '2'],
   ['13905', '358', '364', ' 109', ' 392', ' 134', '2'],
   ['13906', '358', '364', ' 109', ' 393', ' 134', '2'],
   ['13907', '358', '366', ' 113', ' 393', ' 136', '2'],
   ['13908', '358', '367', ' 115', ' 393', ' 138', '2'],
   ['13921', '358', '368', ' 115', ' 402', ' 145', '2'],
   ['13922', '358', '369', ' 114', ' 402', ' 146', '2'],
   ['13923', '358', '369', ' 114', ' 402', ' 146', '2'],
   ['13927', '358', '372', ' 118', ' 405', ' 150', '2'],
   ['13928', '358', '372', ' 118', ' 405', ' 151', '2'],
   ['13929', '358', '374', ' 120', ' 406', ' 151', '2'],
   ['13930', '358', '373', ' 122', ' 405', ' 152', '2'],
   ['13931', '358', '374', ' 124', ' 405', ' 153', '2'],
   ['13932', '358', '375', ' 125', ' 405', ' 153', '2'],
   ['13933', '358', '375', ' 125', ' 406', ' 153', '2'],
   ['13934', '358', '376', ' 127', ' 406', ' 154', '2'],
   ['13935', '358', '376', ' 126', ' 407', ' 155', '2'],
   ['13936', '358', '376', ' 126', ' 409', ' 156', '2'],
   ['13937', '358', '377', ' 127', ' 410', ' 157', '2'],
   ['13938', '358', '376', ' 127', ' 410', ' 158', '2'],
   ['13939', '358', '377', ' 129', ' 410', ' 159', '2'],
   ['13940', '358', '376', ' 129', ' 411', ' 160', '2'],
   ['13943', '358', '377', ' 129', ' 414', ' 163', '2'],
   ['13944', '358', '378', ' 130', ' 415', ' 165', '2'],
   ['13945', '358', '378', ' 131', ' 416', ' 167', '2'],
   ['13946', '358', '379', ' 131', ' 418', ' 168', '2'],
   ['13947', '358', '380', ' 132', ' 418', ' 169', '2'],
   ['13949', '358', '380', ' 133', ' 420', ' 172', '2'],
   ['13950', '358', '382', ' 135', ' 420', ' 173', '2'],
   ['13951', '358', '383', ' 137', ' 422', ' 175', '2'],
   ['13952', '358', '384', ' 139', ' 422', ' 176', '2'],
   ['13953', '358', '384', ' 138', ' 424', ' 177', '2'],
   ['13954', '358', '385', ' 140', ' 424', ' 178', '2'],
   ['13955', '358', '386', ' 141', ' 424', ' 179', '2'],
   ['13956', '358', '385', ' 139', ' 427', ' 181', '2'],
   ['13957', '358', '386', ' 141', ' 427', ' 182', '2'],
   ['13958', '358', '387', ' 143', ' 428', ' 183', '2'],
   ['13959', '358', '387', ' 142', ' 429', ' 185', '2'],
   ['13960', '358', '388', ' 144', ' 430', ' 186', '2'],
   ['13961', '358', '389', ' 146', ' 431', ' 188', '2'],
   ['13962', '358', '390', ' 146', ' 432', ' 189', '2'],
   ['13963', '358', '391', ' 147', ' 433', ' 190', '2'],
   ['13964', '358', '393', ' 148', ' 435', ' 191', '2'],
   ['13965', '358', '392', ' 149', ' 436', ' 194', '2'],
   ['13966', '358', '393', ' 149', ' 438', ' 196', '2'],
   ['13967', '358', '393', ' 149', ' 440', ' 199', '2'],
   ['13968', '358', '394', ' 152', ' 441', ' 201', '2'],
   ['13969', '358', '395', ' 152', ' 443', ' 202', '2'],
   ['13970', '358', '396', ' 153', ' 443', ' 204', '2'],
   ['13971', '358', '397', ' 157', ' 444', ' 206', '2'],
   ['13972', '358', '397', ' 154', ' 448', ' 208', '2'],
   ['13973', '358', '399', ' 157', ' 449', ' 210', '2'],
   ['13974', '358', '400', ' 158', ' 451', ' 213', '2'],
   ['13975', '358', '401', ' 161', ' 452', ' 216', '2'],
   ['13976', '358', '401', ' 161', ' 454', ' 218', '2'],
   ['13977', '358', '402', ' 163', ' 456', ' 220', '2'],
   ['13978', '358', '403', ' 165', ' 458', ' 223', '2'],
   ['13979', '358', '403', ' 166', ' 460', ' 226', '2'],
   ['13980', '358', '403', ' 166', ' 462', ' 228', '2'],
   ['13981', '358', '407', ' 169', ' 465', ' 230', '2'],
   ['13982', '358', '408', ' 169', ' 469', ' 233', '2'],
   ['13983', '358', '408', ' 170', ' 471', ' 236', '2'],
   ['13984', '358', '409', ' 172', ' 474', ' 239', '2'],
   ['13985', '358', '410', ' 173', ' 476', ' 243', '2'],
   ['13986', '358', '411', ' 174', ' 480', ' 247', '2'],
   ['13987', '358', '412', ' 177', ' 483', ' 251', '2'],
   ['13988', '358', '414', ' 179', ' 486', ' 254', '2'],
   ['13989', '358', '417', ' 182', ' 489', ' 258', '2'],
   ['13990', '358', '418', ' 184', ' 492', ' 262', '2'],
   ['13991', '358', '419', ' 185', ' 495', ' 265', '2'],
   ['13992', '358', '421', ' 188', ' 499', ' 270', '2'],
   ['13993', '358', '422', ' 190', ' 502', ' 273', '2'],
   ['13994', '358', '424', ' 193', ' 505', ' 278', '2'],
   ['13995', '358', '425', ' 195', ' 511', ' 284', '2'],
   ['13996', '358', '428', ' 197', ' 515', ' 289', '2'],
   ['13997', '358', '430', ' 200', ' 520', ' 294', '2'],
   ['13998', '358', '432', ' 202', ' 524', ' 300', '2'],
   ['13999', '358', '434', ' 206', ' 528', ' 304', '2'],
   ['14000', '358', '437', ' 210', ' 532', ' 311', '2'],
   ['14001', '358', '440', ' 214', ' 537', ' 316', '2'],
   ['14002', '358', '442', ' 217', ' 543', ' 323', '2'],
   ['14003', '358', '445', ' 220', ' 550', ' 330', '2'],
   ['14006', '358', '453', ' 231', ' 565', ' 349', '2'],
   ['14007', '358', '457', ' 236', ' 574', ' 359', '2'],
   ['14008', '358', '461', ' 242', ' 583', ' 370', '2'],
   ['14009', '358', '464', ' 245', ' 590', ' 378', '2'],
   ['14010', '358', '469', ' 250', ' 598', ' 387', '2'],
   ['14012', '358', '477', ' 261', ' 615', ' 408', '2'],
   ['14013', '358', '483', ' 267', ' 622', ' 413', '2'],
   ['14014', '358', '492', ' 272', ' 630', ' 415', '2'],
   ['14015', '358', '504', ' 278', ' 642', ' 418', '2'],
   ['14016', '358', '508', ' 285', ' 638', ' 415', '2'],
   ['14017', '358', '517', ' 293', ' 641', ' 413', '2'],
   ['14018', '358', '526', ' 301', ' 646', ' 413', '2'],
   ['14019', '358', '534', ' 309', ' 651', ' 414', '2'],
   ['14020', '358', '541', ' 317', ' 655', ' 413', '2'],
   ['14021', '358', '553', ' 322', ' 665', ' 413', '2'],
   ['14022', '358', '565', ' 335', ' 667', ' 413', '2']]},
 {'360': [['13953', '360', '381', ' 107', ' 409', ' 129', '2'],
   ['13954', '360', '381', ' 107', ' 408', ' 129', '2'],
   ['13955', '360', '381', ' 107', ' 408', ' 129', '2'],
   ['13956', '360', '381', ' 108', ' 408', ' 130', '2'],
   ['13957', '360', '381', ' 108', ' 409', ' 130', '2'],
   ['13958', '360', '381', ' 108', ' 409', ' 131', '2'],
   ['13959', '360', '381', ' 108', ' 409', ' 131', '2'],
   ['13960', '360', '381', ' 107', ' 409', ' 131', '2'],
   ['13961', '360', '381', ' 107', ' 410', ' 131', '2'],
   ['13962', '360', '382', ' 107', ' 410', ' 131', '2'],
   ['13963', '360', '381', ' 107', ' 410', ' 132', '2'],
   ['13964', '360', '382', ' 108', ' 410', ' 132', '2'],
   ['13965', '360', '382', ' 108', ' 411', ' 133', '2'],
   ['13966', '360', '383', ' 109', ' 411', ' 133', '2'],
   ['13970', '360', '384', ' 109', ' 413', ' 134', '2'],
   ['13971', '360', '386', ' 111', ' 412', ' 135', '2'],
   ['13975', '360', '388', ' 113', ' 414', ' 137', '2'],
   ['13976', '360', '389', ' 115', ' 414', ' 137', '2'],
   ['13977', '360', '390', ' 117', ' 414', ' 137', '2'],
   ['13978', '360', '389', ' 117', ' 414', ' 138', '2'],
   ['13979', '360', '388', ' 116', ' 414', ' 139', '2'],
   ['13980', '360', '388', ' 117', ' 414', ' 139', '2'],
   ['13981', '360', '390', ' 117', ' 415', ' 139', '2'],
   ['13982', '360', '389', ' 116', ' 417', ' 140', '2'],
   ['13983', '360', '390', ' 117', ' 417', ' 140', '2'],
   ['13984', '360', '392', ' 119', ' 417', ' 140', '2'],
   ['13985', '360', '393', ' 120', ' 418', ' 141', '2'],
   ['13986', '360', '392', ' 120', ' 418', ' 141', '2'],
   ['13987', '360', '391', ' 118', ' 419', ' 141', '2'],
   ['13988', '360', '391', ' 117', ' 419', ' 140', '2'],
   ['13989', '360', '391', ' 116', ' 421', ' 141', '2'],
   ['13990', '360', '391', ' 115', ' 422', ' 141', '2'],
   ['13991', '360', '390', ' 114', ' 422', ' 142', '2'],
   ['13992', '360', '391', ' 114', ' 423', ' 142', '2'],
   ['13993', '360', '393', ' 116', ' 423', ' 142', '2'],
   ['13994', '360', '393', ' 118', ' 422', ' 143', '2'],
   ['14003', '360', '400', ' 126', ' 424', ' 147', '2'],
   ['14004', '360', '399', ' 126', ' 426', ' 148', '2'],
   ['14006', '360', '399', ' 126', ' 427', ' 148', '2'],
   ['14007', '360', '398', ' 124', ' 430', ' 149', '2'],
   ['14008', '360', '398', ' 124', ' 432', ' 150', '2'],
   ['14009', '360', '398', ' 125', ' 432', ' 152', '2'],
   ['14010', '360', '399', ' 126', ' 433', ' 152', '2'],
   ['14011', '360', '400', ' 126', ' 433', ' 152', '2'],
   ['14012', '360', '401', ' 127', ' 433', ' 152', '2'],
   ['14013', '360', '402', ' 128', ' 434', ' 153', '2'],
   ['14014', '360', '402', ' 128', ' 435', ' 153', '2'],
   ['14015', '360', '401', ' 128', ' 435', ' 154', '2'],
   ['14016', '360', '403', ' 130', ' 435', ' 154', '2'],
   ['14017', '360', '403', ' 131', ' 435', ' 155', '2'],
   ['14019', '360', '402', ' 129', ' 438', ' 156', '2'],
   ['14020', '360', '402', ' 129', ' 438', ' 156', '2'],
   ['14021', '360', '402', ' 127', ' 439', ' 156', '2'],
   ['14022', '360', '401', ' 126', ' 441', ' 157', '2'],
   ['14023', '360', '401', ' 125', ' 441', ' 158', '2'],
   ['14024', '360', '402', ' 126', ' 441', ' 158', '2'],
   ['14025', '360', '402', ' 126', ' 442', ' 159', '2'],
   ['14026', '360', '403', ' 127', ' 442', ' 160', '2'],
   ['14027', '360', '404', ' 129', ' 441', ' 161', '2'],
   ['14028', '360', '406', ' 132', ' 441', ' 162', '2'],
   ['14029', '360', '406', ' 129', ' 444', ' 163', '2'],
   ['14030', '360', '406', ' 130', ' 446', ' 164', '2'],
   ['14031', '360', '407', ' 129', ' 447', ' 165', '2'],
   ['14032', '360', '408', ' 130', ' 448', ' 165', '2'],
   ['14033', '360', '408', ' 131', ' 448', ' 166', '2'],
   ['14034', '360', '408', ' 132', ' 449', ' 167', '2'],
   ['14035', '360', '409', ' 133', ' 449', ' 168', '2'],
   ['14036', '360', '412', ' 136', ' 450', ' 168', '2'],
   ['14037', '360', '412', ' 137', ' 450', ' 169', '2'],
   ['14038', '360', '412', ' 138', ' 449', ' 170', '2'],
   ['14039', '360', '412', ' 138', ' 451', ' 171', '2'],
   ['14040', '360', '413', ' 139', ' 452', ' 171', '2'],
   ['14041', '360', '413', ' 139', ' 453', ' 173', '2'],
   ['14042', '360', '413', ' 139', ' 454', ' 174', '2'],
   ['14043', '360', '414', ' 141', ' 454', ' 175', '2'],
   ['14044', '360', '415', ' 141', ' 456', ' 176', '2'],
   ['14045', '360', '417', ' 143', ' 457', ' 177', '2'],
   ['14046', '360', '417', ' 144', ' 458', ' 178', '2'],
   ['14047', '360', '417', ' 144', ' 459', ' 179', '2'],
   ['14048', '360', '419', ' 144', ' 460', ' 180', '2'],
   ['14049', '360', '418', ' 145', ' 461', ' 181', '2'],
   ['14050', '360', '419', ' 145', ' 462', ' 182', '2'],
   ['14051', '360', '420', ' 146', ' 463', ' 183', '2'],
   ['14052', '360', '420', ' 146', ' 465', ' 184', '2'],
   ['14053', '360', '421', ' 146', ' 466', ' 185', '2'],
   ['14054', '360', '422', ' 147', ' 467', ' 187', '2'],
   ['14055', '360', '422', ' 147', ' 468', ' 188', '2'],
   ['14056', '360', '422', ' 146', ' 470', ' 189', '2'],
   ['14057', '360', '424', ' 149', ' 470', ' 190', '2'],
   ['14058', '360', '425', ' 150', ' 472', ' 191', '2'],
   ['14059', '360', '427', ' 151', ' 474', ' 192', '2'],
   ['14060', '360', '427', ' 151', ' 475', ' 194', '2'],
   ['14061', '360', '428', ' 153', ' 475', ' 195', '2'],
   ['14062', '360', '429', ' 153', ' 477', ' 197', '2'],
   ['14063', '360', '429', ' 154', ' 479', ' 199', '2'],
   ['14064', '360', '431', ' 155', ' 481', ' 200', '2'],
   ['14065', '360', '431', ' 155', ' 482', ' 202', '2'],
   ['14066', '360', '432', ' 156', ' 483', ' 204', '2'],
   ['14067', '360', '434', ' 158', ' 485', ' 205', '2'],
   ['14068', '360', '436', ' 159', ' 486', ' 206', '2'],
   ['14069', '360', '438', ' 161', ' 487', ' 207', '2'],
   ['14070', '360', '439', ' 162', ' 488', ' 208', '2'],
   ['14071', '360', '440', ' 163', ' 491', ' 210', '2'],
   ['14072', '360', '440', ' 163', ' 493', ' 211', '2'],
   ['14073', '360', '440', ' 164', ' 494', ' 213', '2'],
   ['14074', '360', '440', ' 165', ' 496', ' 215', '2'],
   ['14075', '360', '440', ' 165', ' 498', ' 219', '2'],
   ['14076', '360', '441', ' 165', ' 500', ' 220', '2'],
   ['14077', '360', '442', ' 168', ' 501', ' 222', '2'],
   ['14078', '360', '444', ' 169', ' 504', ' 225', '2'],
   ['14079', '360', '445', ' 170', ' 507', ' 227', '2'],
   ['14080', '360', '448', ' 171', ' 509', ' 228', '2'],
   ['14081', '360', '451', ' 176', ' 510', ' 229', '2'],
   ['14082', '360', '451', ' 175', ' 512', ' 231', '2'],
   ['14083', '360', '453', ' 176', ' 516', ' 235', '2'],
   ['14084', '360', '454', ' 178', ' 518', ' 237', '2'],
   ['14085', '360', '454', ' 179', ' 521', ' 239', '2'],
   ['14086', '360', '457', ' 182', ' 522', ' 242', '2'],
   ['14087', '360', '458', ' 185', ' 524', ' 246', '2'],
   ['14088', '360', '459', ' 186', ' 527', ' 248', '2'],
   ['14089', '360', '463', ' 189', ' 530', ' 251', '2'],
   ['14090', '360', '464', ' 190', ' 533', ' 253', '2'],
   ['14091', '360', '468', ' 193', ' 534', ' 254', '2'],
   ['14092', '360', '469', ' 195', ' 537', ' 257', '2'],
   ['14093', '360', '470', ' 197', ' 542', ' 262', '2'],
   ['14094', '360', '472', ' 199', ' 543', ' 264', '2'],
   ['14095', '360', '472', ' 200', ' 548', ' 268', '2'],
   ['14096', '360', '472', ' 200', ' 552', ' 271', '2'],
   ['14097', '360', '477', ' 206', ' 554', ' 274', '2'],
   ['14098', '360', '477', ' 205', ' 559', ' 277', '2'],
   ['14099', '360', '478', ' 204', ' 563', ' 279', '2'],
   ['14100', '360', '486', ' 213', ' 566', ' 284', '2'],
   ['14101', '360', '482', ' 207', ' 572', ' 288', '2'],
   ['14102', '360', '483', ' 208', ' 578', ' 293', '2'],
   ['14103', '360', '485', ' 209', ' 582', ' 297', '2'],
   ['14104', '360', '488', ' 212', ' 585', ' 299', '2'],
   ['14105', '360', '491', ' 216', ' 589', ' 305', '2'],
   ['14106', '360', '494', ' 218', ' 594', ' 308', '2'],
   ['14107', '360', '496', ' 220', ' 599', ' 313', '2'],
   ['14108', '360', '498', ' 222', ' 605', ' 319', '2'],
   ['14109', '360', '501', ' 224', ' 610', ' 323', '2'],
   ['14110', '360', '504', ' 226', ' 616', ' 329', '2'],
   ['14111', '360', '508', ' 231', ' 620', ' 334', '2'],
   ['14112', '360', '511', ' 234', ' 628', ' 341', '2'],
   ['14113', '360', '515', ' 238', ' 633', ' 347', '2'],
   ['14114', '360', '518', ' 241', ' 639', ' 353', '2'],
   ['14115', '360', '522', ' 245', ' 646', ' 360', '2'],
   ['14116', '360', '526', ' 251', ' 652', ' 367', '2'],
   ['14117', '360', '530', ' 252', ' 661', ' 375', '2'],
   ['14118', '360', '535', ' 256', ' 669', ' 382', '2'],
   ['14119', '360', '537', ' 261', ' 678', ' 393', '2'],
   ['14120', '360', '541', ' 265', ' 686', ' 402', '2'],
   ['14121', '360', '547', ' 269', ' 693', ' 407', '2'],
   ['14122', '360', '553', ' 273', ' 700', ' 412', '2'],
   ['14123', '360', '562', ' 278', ' 709', ' 414', '2'],
   ['14124', '360', '574', ' 282', ' 721', ' 416', '2'],
   ['14125', '360', '582', ' 288', ' 726', ' 417', '2'],
   ['14126', '360', '589', ' 295', ' 728', ' 416', '2'],
   ['14127', '360', '595', ' 301', ' 732', ' 417', '2'],
   ['14128', '360', '604', ' 308', ' 732', ' 414', '2'],
   ['14129', '360', '613', ' 315', ' 738', ' 413', '2'],
   ['14130', '360', '621', ' 320', ' 745', ' 414', '2'],
   ['14131', '360', '628', ' 323', ' 751', ' 413', '2'],
   ['14132', '360', '638', ' 333', ' 752', ' 413', '2'],
   ['14133', '360', '646', ' 343', ' 751', ' 413', '2'],
   ['14135', '360', '666', ' 360', ' 753', ' 414', '2']]},
 {'389': [['14464', '389', '366', ' 105', ' 389', ' 119', '2'],
   ['14465', '389', '366', ' 104', ' 390', ' 119', '2'],
   ['14466', '389', '366', ' 104', ' 390', ' 119', '2'],
   ['14467', '389', '367', ' 104', ' 390', ' 119', '2'],
   ['14468', '389', '368', ' 105', ' 390', ' 119', '2'],
   ['14469', '389', '368', ' 106', ' 390', ' 119', '2'],
   ['14470', '389', '368', ' 105', ' 390', ' 119', '2'],
   ['14471', '389', '368', ' 105', ' 390', ' 118', '2'],
   ['14472', '389', '368', ' 105', ' 390', ' 118', '2'],
   ['14473', '389', '368', ' 106', ' 390', ' 119', '2'],
   ['14477', '389', '369', ' 106', ' 389', ' 118', '2'],
   ['14478', '389', '368', ' 107', ' 390', ' 119', '2'],
   ['14479', '389', '369', ' 107', ' 390', ' 119', '2'],
   ['14483', '389', '369', ' 106', ' 391', ' 119', '2'],
   ['14484', '389', '369', ' 106', ' 391', ' 119', '2'],
   ['14485', '389', '370', ' 107', ' 392', ' 120', '2'],
   ['14486', '389', '370', ' 107', ' 392', ' 120', '2'],
   ['14487', '389', '370', ' 107', ' 393', ' 120', '2'],
   ['14488', '389', '369', ' 107', ' 394', ' 121', '2'],
   ['14489', '389', '369', ' 107', ' 393', ' 121', '2'],
   ['14490', '389', '369', ' 106', ' 393', ' 121', '2'],
   ['14496', '389', '368', ' 106', ' 394', ' 121', '2'],
   ['14497', '389', '369', ' 106', ' 394', ' 121', '2'],
   ['14498', '389', '370', ' 106', ' 393', ' 121', '2'],
   ['14499', '389', '370', ' 106', ' 393', ' 120', '2'],
   ['14500', '389', '370', ' 106', ' 393', ' 120', '2'],
   ['14501', '389', '370', ' 106', ' 393', ' 120', '2'],
   ['14502', '389', '370', ' 106', ' 394', ' 121', '2'],
   ['14513', '389', '370', ' 107', ' 395', ' 122', '2'],
   ['14514', '389', '370', ' 107', ' 396', ' 122', '2'],
   ['14515', '389', '369', ' 107', ' 397', ' 123', '2'],
   ['14516', '389', '369', ' 107', ' 397', ' 123', '2'],
   ['14517', '389', '369', ' 106', ' 397', ' 124', '2'],
   ['14518', '389', '369', ' 106', ' 398', ' 124', '2'],
   ['14519', '389', '369', ' 105', ' 398', ' 124', '2'],
   ['14520', '389', '368', ' 104', ' 399', ' 124', '2'],
   ['14521', '389', '368', ' 104', ' 400', ' 125', '2'],
   ['14522', '389', '370', ' 105', ' 400', ' 125', '2'],
   ['14523', '389', '371', ' 105', ' 400', ' 125', '2'],
   ['14524', '389', '371', ' 105', ' 400', ' 125', '2'],
   ['14525', '389', '372', ' 107', ' 399', ' 125', '2'],
   ['14526', '389', '373', ' 108', ' 398', ' 125', '2'],
   ['14527', '389', '373', ' 109', ' 398', ' 126', '2'],
   ['14528', '389', '373', ' 109', ' 398', ' 126', '2'],
   ['14529', '389', '373', ' 109', ' 398', ' 126', '2'],
   ['14530', '389', '374', ' 109', ' 398', ' 126', '2'],
   ['14531', '389', '374', ' 110', ' 398', ' 126', '2'],
   ['14532', '389', '375', ' 110', ' 398', ' 126', '2'],
   ['14533', '389', '375', ' 110', ' 398', ' 126', '2'],
   ['14534', '389', '375', ' 111', ' 398', ' 126', '2'],
   ['14535', '389', '374', ' 110', ' 399', ' 126', '2'],
   ['14536', '389', '374', ' 110', ' 399', ' 127', '2'],
   ['14537', '389', '374', ' 110', ' 399', ' 126', '2'],
   ['14538', '389', '374', ' 110', ' 399', ' 127', '2'],
   ['14539', '389', '374', ' 110', ' 398', ' 127', '2'],
   ['14546', '389', '376', ' 114', ' 400', ' 130', '2'],
   ['14547', '389', '376', ' 114', ' 402', ' 131', '2'],
   ['14548', '389', '375', ' 113', ' 403', ' 132', '2'],
   ['14549', '389', '375', ' 112', ' 403', ' 132', '2'],
   ['14550', '389', '375', ' 112', ' 403', ' 132', '2'],
   ['14551', '389', '375', ' 113', ' 402', ' 132', '2'],
   ['14553', '389', '375', ' 113', ' 403', ' 133', '2'],
   ['14554', '389', '375', ' 113', ' 403', ' 133', '2'],
   ['14555', '389', '375', ' 113', ' 403', ' 133', '2'],
   ['14557', '389', '375', ' 112', ' 405', ' 133', '2'],
   ['14558', '389', '375', ' 112', ' 405', ' 134', '2'],
   ['14559', '389', '376', ' 113', ' 405', ' 134', '2'],
   ['14560', '389', '377', ' 113', ' 405', ' 134', '2'],
   ['14561', '389', '376', ' 113', ' 405', ' 134', '2'],
   ['14562', '389', '377', ' 114', ' 405', ' 134', '2'],
   ['14563', '389', '377', ' 114', ' 405', ' 134', '2'],
   ['14564', '389', '377', ' 114', ' 405', ' 134', '2'],
   ['14565', '389', '376', ' 113', ' 406', ' 134', '2'],
   ['14566', '389', '377', ' 113', ' 407', ' 135', '2'],
   ['14567', '389', '378', ' 113', ' 408', ' 135', '2'],
   ['14568', '389', '378', ' 113', ' 409', ' 135', '2'],
   ['14569', '389', '378', ' 113', ' 409', ' 135', '2'],
   ['14570', '389', '378', ' 113', ' 409', ' 136', '2'],
   ['14571', '389', '378', ' 113', ' 409', ' 136', '2'],
   ['14572', '389', '378', ' 113', ' 410', ' 137', '2'],
   ['14573', '389', '378', ' 113', ' 410', ' 137', '2'],
   ['14574', '389', '377', ' 111', ' 411', ' 137', '2'],
   ['14575', '389', '377', ' 111', ' 412', ' 137', '2'],
   ['14576', '389', '377', ' 111', ' 412', ' 137', '2'],
   ['14577', '389', '377', ' 110', ' 413', ' 138', '2'],
   ['14578', '389', '377', ' 109', ' 413', ' 138', '2'],
   ['14579', '389', '378', ' 109', ' 413', ' 138', '2'],
   ['14580', '389', '379', ' 111', ' 413', ' 138', '2'],
   ['14581', '389', '380', ' 111', ' 414', ' 139', '2'],
   ['14582', '389', '381', ' 111', ' 414', ' 139', '2'],
   ['14583', '389', '381', ' 111', ' 414', ' 139', '2'],
   ['14584', '389', '381', ' 111', ' 414', ' 139', '2'],
   ['14585', '389', '381', ' 111', ' 414', ' 139', '2'],
   ['14586', '389', '382', ' 111', ' 414', ' 139', '2'],
   ['14587', '389', '382', ' 111', ' 415', ' 139', '2'],
   ['14588', '389', '382', ' 112', ' 414', ' 139', '2'],
   ['14589', '389', '383', ' 112', ' 415', ' 139', '2'],
   ['14599', '389', '385', ' 117', ' 416', ' 143', '2'],
   ['14600', '389', '386', ' 118', ' 417', ' 144', '2'],
   ['14601', '389', '387', ' 119', ' 417', ' 144', '2'],
   ['14604', '389', '389', ' 122', ' 416', ' 145', '2'],
   ['14607', '389', '389', ' 122', ' 417', ' 145', '2'],
   ['14608', '389', '389', ' 122', ' 418', ' 145', '2'],
   ['14609', '389', '389', ' 121', ' 419', ' 145', '2'],
   ['14610', '389', '389', ' 121', ' 419', ' 146', '2'],
   ['14611', '389', '389', ' 121', ' 420', ' 146', '2'],
   ['14612', '389', '390', ' 121', ' 420', ' 147', '2'],
   ['14613', '389', '390', ' 121', ' 420', ' 147', '2'],
   ['14614', '389', '390', ' 122', ' 420', ' 147', '2'],
   ['14615', '389', '390', ' 122', ' 420', ' 148', '2'],
   ['14616', '389', '390', ' 123', ' 421', ' 148', '2'],
   ['14617', '389', '391', ' 123', ' 422', ' 149', '2'],
   ['14618', '389', '391', ' 125', ' 422', ' 149', '2'],
   ['14619', '389', '392', ' 125', ' 422', ' 150', '2'],
   ['14620', '389', '392', ' 124', ' 424', ' 150', '2'],
   ['14621', '389', '391', ' 124', ' 425', ' 151', '2'],
   ['14622', '389', '391', ' 124', ' 425', ' 151', '2'],
   ['14623', '389', '391', ' 126', ' 424', ' 152', '2'],
   ['14624', '389', '392', ' 126', ' 425', ' 152', '2'],
   ['14625', '389', '392', ' 126', ' 425', ' 152', '2'],
   ['14626', '389', '392', ' 127', ' 425', ' 152', '2'],
   ['14627', '389', '393', ' 127', ' 426', ' 152', '2'],
   ['14628', '389', '393', ' 126', ' 427', ' 153', '2'],
   ['14629', '389', '393', ' 126', ' 428', ' 153', '2'],
   ['14630', '389', '393', ' 126', ' 429', ' 154', '2'],
   ['14631', '389', '393', ' 126', ' 429', ' 155', '2'],
   ['14632', '389', '393', ' 126', ' 429', ' 155', '2'],
   ['14633', '389', '394', ' 127', ' 430', ' 156', '2'],
   ['14634', '389', '395', ' 127', ' 431', ' 156', '2'],
   ['14635', '389', '396', ' 128', ' 432', ' 157', '2'],
   ['14636', '389', '395', ' 128', ' 432', ' 157', '2'],
   ['14637', '389', '396', ' 129', ' 432', ' 158', '2'],
   ['14638', '389', '396', ' 129', ' 432', ' 158', '2'],
   ['14639', '389', '396', ' 129', ' 433', ' 158', '2'],
   ['14640', '389', '397', ' 129', ' 434', ' 159', '2'],
   ['14641', '389', '397', ' 129', ' 434', ' 159', '2'],
   ['14642', '389', '398', ' 131', ' 433', ' 159', '2'],
   ['14643', '389', '399', ' 131', ' 434', ' 160', '2'],
   ['14644', '389', '398', ' 131', ' 434', ' 160', '2'],
   ['14645', '389', '399', ' 131', ' 435', ' 161', '2'],
   ['14646', '389', '399', ' 132', ' 435', ' 161', '2'],
   ['14647', '389', '400', ' 133', ' 437', ' 163', '2'],
   ['14648', '389', '400', ' 133', ' 438', ' 164', '2'],
   ['14649', '389', '399', ' 133', ' 438', ' 164', '2'],
   ['14650', '389', '399', ' 133', ' 438', ' 165', '2'],
   ['14651', '389', '399', ' 134', ' 438', ' 165', '2'],
   ['14652', '389', '400', ' 134', ' 440', ' 166', '2'],
   ['14653', '389', '400', ' 134', ' 441', ' 166', '2'],
   ['14654', '389', '400', ' 134', ' 441', ' 167', '2'],
   ['14655', '389', '401', ' 135', ' 441', ' 168', '2'],
   ['14656', '389', '400', ' 135', ' 443', ' 169', '2'],
   ['14657', '389', '400', ' 135', ' 443', ' 170', '2'],
   ['14658', '389', '401', ' 135', ' 443', ' 170', '2'],
   ['14659', '389', '403', ' 137', ' 444', ' 171', '2'],
   ['14660', '389', '403', ' 138', ' 444', ' 171', '2'],
   ['14661', '389', '403', ' 138', ' 444', ' 171', '2'],
   ['14662', '389', '403', ' 138', ' 444', ' 172', '2'],
   ['14663', '389', '404', ' 139', ' 444', ' 172', '2'],
   ['14664', '389', '405', ' 141', ' 445', ' 173', '2'],
   ['14665', '389', '406', ' 141', ' 446', ' 173', '2'],
   ['14666', '389', '406', ' 141', ' 447', ' 174', '2'],
   ['14667', '389', '405', ' 140', ' 449', ' 175', '2'],
   ['14668', '389', '405', ' 140', ' 450', ' 176', '2'],
   ['14669', '389', '406', ' 140', ' 450', ' 177', '2'],
   ['14670', '389', '407', ' 141', ' 450', ' 177', '2'],
   ['14671', '389', '407', ' 142', ' 450', ' 177', '2'],
   ['14672', '389', '407', ' 142', ' 451', ' 178', '2'],
   ['14673', '389', '407', ' 142', ' 452', ' 179', '2'],
   ['14674', '389', '408', ' 142', ' 455', ' 181', '2'],
   ['14675', '389', '408', ' 143', ' 454', ' 181', '2'],
   ['14676', '389', '408', ' 143', ' 453', ' 181', '2'],
   ['14677', '389', '410', ' 146', ' 454', ' 184', '2'],
   ['14678', '389', '409', ' 146', ' 455', ' 185', '2'],
   ['14679', '389', '409', ' 146', ' 456', ' 186', '2'],
   ['14680', '389', '410', ' 146', ' 456', ' 186', '2'],
   ['14681', '389', '411', ' 148', ' 456', ' 187', '2'],
   ['14682', '389', '411', ' 148', ' 457', ' 187', '2'],
   ['14683', '389', '412', ' 149', ' 457', ' 188', '2'],
   ['14684', '389', '413', ' 149', ' 458', ' 188', '2'],
   ['14685', '389', '412', ' 149', ' 459', ' 189', '2'],
   ['14686', '389', '413', ' 149', ' 461', ' 190', '2'],
   ['14687', '389', '413', ' 149', ' 462', ' 191', '2'],
   ['14688', '389', '413', ' 148', ' 462', ' 192', '2'],
   ['14689', '389', '413', ' 148', ' 463', ' 193', '2'],
   ['14690', '389', '414', ' 149', ' 463', ' 193', '2'],
   ['14691', '389', '415', ' 150', ' 464', ' 194', '2'],
   ['14692', '389', '414', ' 150', ' 466', ' 197', '2'],
   ['14693', '389', '414', ' 150', ' 466', ' 198', '2'],
   ['14694', '389', '414', ' 151', ' 467', ' 199', '2'],
   ['14695', '389', '415', ' 152', ' 466', ' 200', '2'],
   ['14696', '389', '416', ' 153', ' 467', ' 201', '2'],
   ['14697', '389', '417', ' 154', ' 468', ' 202', '2'],
   ['14698', '389', '417', ' 155', ' 468', ' 203', '2'],
   ['14699', '389', '419', ' 156', ' 469', ' 203', '2'],
   ['14700', '389', '418', ' 157', ' 469', ' 205', '2'],
   ['14701', '389', '419', ' 158', ' 471', ' 206', '2'],
   ['14702', '389', '420', ' 158', ' 471', ' 207', '2'],
   ['14703', '389', '420', ' 159', ' 472', ' 208', '2'],
   ['14704', '389', '420', ' 160', ' 473', ' 210', '2'],
   ['14705', '389', '421', ' 161', ' 474', ' 211', '2'],
   ['14706', '389', '422', ' 161', ' 474', ' 210', '2'],
   ['14707', '389', '422', ' 162', ' 474', ' 211', '2'],
   ['14708', '389', '422', ' 162', ' 477', ' 213', '2'],
   ['14709', '389', '423', ' 162', ' 479', ' 216', '2'],
   ['14710', '389', '424', ' 164', ' 480', ' 218', '2'],
   ['14711', '389', '424', ' 164', ' 482', ' 220', '2'],
   ['14712', '389', '425', ' 165', ' 483', ' 221', '2'],
   ['14713', '389', '425', ' 167', ' 484', ' 223', '2'],
   ['14714', '389', '427', ' 168', ' 484', ' 223', '2'],
   ['14715', '389', '427', ' 168', ' 484', ' 223', '2'],
   ['14716', '389', '427', ' 168', ' 485', ' 224', '2'],
   ['14717', '389', '427', ' 169', ' 486', ' 226', '2'],
   ['14718', '389', '428', ' 170', ' 488', ' 228', '2'],
   ['14719', '389', '429', ' 171', ' 491', ' 230', '2'],
   ['14720', '389', '429', ' 171', ' 493', ' 232', '2'],
   ['14721', '389', '430', ' 172', ' 495', ' 233', '2'],
   ['14722', '389', '430', ' 172', ' 496', ' 235', '2'],
   ['14723', '389', '430', ' 173', ' 497', ' 236', '2'],
   ['14724', '389', '432', ' 175', ' 497', ' 237', '2'],
   ['14725', '389', '431', ' 175', ' 500', ' 239', '2'],
   ['14726', '389', '431', ' 175', ' 502', ' 242', '2'],
   ['14727', '389', '433', ' 176', ' 504', ' 243', '2'],
   ['14728', '389', '434', ' 178', ' 506', ' 247', '2'],
   ['14729', '389', '436', ' 182', ' 508', ' 249', '2'],
   ['14730', '389', '437', ' 183', ' 508', ' 250', '2'],
   ['14731', '389', '437', ' 186', ' 509', ' 253', '2'],
   ['14732', '389', '438', ' 187', ' 511', ' 255', '2'],
   ['14733', '389', '440', ' 190', ' 513', ' 257', '2'],
   ['14734', '389', '439', ' 190', ' 516', ' 261', '2'],
   ['14735', '389', '441', ' 190', ' 519', ' 261', '2'],
   ['14736', '389', '440', ' 189', ' 523', ' 265', '2'],
   ['14737', '389', '441', ' 191', ' 525', ' 269', '2'],
   ['14738', '389', '443', ' 192', ' 527', ' 270', '2'],
   ['14739', '389', '443', ' 193', ' 530', ' 274', '2'],
   ['14740', '389', '446', ' 194', ' 532', ' 275', '2'],
   ['14741', '389', '447', ' 196', ' 535', ' 278', '2'],
   ['14742', '389', '449', ' 199', ' 537', ' 281', '2'],
   ['14743', '389', '450', ' 200', ' 538', ' 283', '2'],
   ['14744', '389', '451', ' 202', ' 541', ' 285', '2'],
   ['14745', '389', '450', ' 203', ' 546', ' 292', '2'],
   ['14746', '389', '452', ' 206', ' 548', ' 296', '2'],
   ['14747', '389', '455', ' 208', ' 551', ' 297', '2'],
   ['14748', '389', '457', ' 211', ' 553', ' 300', '2'],
   ['14749', '389', '458', ' 214', ' 555', ' 304', '2'],
   ['14750', '389', '460', ' 216', ' 559', ' 307', '2'],
   ['14751', '389', '461', ' 217', ' 562', ' 310', '2'],
   ['14752', '389', '463', ' 219', ' 566', ' 313', '2'],
   ['14753', '389', '464', ' 220', ' 570', ' 317', '2'],
   ['14754', '389', '466', ' 223', ' 574', ' 322', '2'],
   ['14755', '389', '468', ' 224', ' 579', ' 325', '2'],
   ['14756', '389', '470', ' 226', ' 583', ' 330', '2'],
   ['14757', '389', '472', ' 228', ' 587', ' 334', '2'],
   ['14758', '389', '475', ' 231', ' 591', ' 338', '2'],
   ['14759', '389', '476', ' 235', ' 595', ' 344', '2'],
   ['14760', '389', '480', ' 238', ' 600', ' 348', '2'],
   ['14761', '389', '482', ' 241', ' 605', ' 354', '2'],
   ['14762', '389', '484', ' 243', ' 610', ' 359', '2'],
   ['14763', '389', '486', ' 245', ' 615', ' 364', '2'],
   ['14764', '389', '488', ' 247', ' 619', ' 369', '2'],
   ['14765', '389', '490', ' 251', ' 625', ' 376', '2'],
   ['14766', '389', '493', ' 254', ' 632', ' 383', '2'],
   ['14767', '389', '496', ' 257', ' 638', ' 389', '2'],
   ['14768', '389', '498', ' 260', ' 645', ' 398', '2'],
   ['14769', '389', '502', ' 264', ' 652', ' 406', '2'],
   ['14770', '389', '506', ' 267', ' 656', ' 410', '2'],
   ['14771', '389', '511', ' 271', ' 660', ' 412', '2'],
   ['14772', '389', '516', ' 275', ' 663', ' 414', '2'],
   ['14773', '389', '522', ' 279', ' 667', ' 414', '2'],
   ['14774', '389', '527', ' 282', ' 672', ' 414', '2'],
   ['14775', '389', '534', ' 287', ' 677', ' 414', '2'],
   ['14776', '389', '539', ' 291', ' 680', ' 415', '2'],
   ['14777', '389', '543', ' 295', ' 680', ' 412', '2'],
   ['14778', '389', '550', ' 301', ' 683', ' 411', '2']]}]


In [5]:

main_process_video_clip_creator(voilation_id_tracker,violation_frame_tracker,evidance_clip_dir_paths,'30_05_2024_infenrence_output/all_frames_record',violation_coordinates_json)

Exception in thread Thread-142 (sub_process_video_clip_creator):
Traceback (most recent call last):
  File "/usr/lib/python3.11/threading.py", line 1045, in _bootstrap_inner
    self.run()
  File "/home/hlink/workspace/learning/boxmot/bmt/lib/python3.11/site-packages/ipykernel/ipkernel.py", line 766, in run_closure
    _threading_Thread_run(self)
  File "/usr/lib/python3.11/threading.py", line 982, in run
    self._target(*self._args, **self._kwargs)
  File "/home/hlink/workspace/learning/boxmot/utils/mt_video_utils.py", line 13, in sub_process_video_clip_creator
    previous_frames,post_frames=frame_picker(violation_frame_tracker[entry[0]],all_frames_record_path,window_size)
                                             ~~~~~~~~~~~~~~~~~~~~~~~^^^^^^^^^^
TypeError: tuple indices must be integers or slices, not dict


PRitning from video clips


[{'2': [['67', '2', '364', ' 101', ' 388', ' 121', '2'],
   ['68', '2', '365', ' 103', ' 387', ' 120', '2'],
   ['74', '2', '366', ' 104', ' 390', ' 122', '2'],
   ['75', '2', '366', ' 104', ' 391', ' 123', '2'],
   ['76', '2', '366', ' 104', ' 392', ' 124', '2'],
   ['77', '2', '365', ' 104', ' 392', ' 124', '2'],
   ['78', '2', '366', ' 104', ' 391', ' 124', '2'],
   ['79', '2', '365', ' 104', ' 391', ' 124', '2'],
   ['80', '2', '365', ' 103', ' 393', ' 124', '2'],
   ['81', '2', '365', ' 103', ' 394', ' 125', '2'],
   ['82', '2', '365', ' 103', ' 395', ' 126', '2'],
   ['83', '2', '365', ' 103', ' 396', ' 126', '2'],
   ['84', '2', '365', ' 103', ' 396', ' 127', '2'],
   ['85', '2', '365', ' 103', ' 396', ' 127', '2'],
   ['86', '2', '366', ' 103', ' 396', ' 127', '2'],
   ['87', '2', '366', ' 103', ' 396', ' 127', '2'],
   ['88', '2', '366', ' 103', ' 397', ' 127', '2'],
   ['89', '2', '366', ' 102', ' 397', ' 127', '2'],
   ['90', '2', '366', ' 102', ' 398', ' 127', '2'],
   ['91